In [64]:
# Generic imports
import pandas as pd
from typing import Tuple, cast
import plotly.express as px
import warnings

warnings.filterwarnings("ignore")

In [65]:
# Local imports - see https://github.com/jakee417/bayesian-opt/tree/master
from thompson_sampling import PathwiseThompsonSampling
from plotting_helpers import *

In [66]:
# Ax & BoTorch imports
from ax.service.ax_client import AxClient, ObjectiveProperties
from ax.modelbridge.generation_strategy import GenerationStep, GenerationStrategy
from ax.models.torch.botorch_modular.surrogate import Surrogate
from ax.modelbridge.registry import Models
from ax.utils.common.typeutils import not_none
from ax.core.types import TParameterization, TEvaluationOutcome, TModelPredict
from ax.core.observation import ObservationFeatures
from ax.modelbridge import TorchModelBridge
from ax.plot.diagnostic import interact_cross_validation_plotly
from ax.plot.contour import interact_contour_plotly
from ax.utils.notebook.plotting import render
from ax.modelbridge.cross_validation import cross_validate, compute_diagnostics
from botorch.acquisition.analytic import (
    ProbabilityOfImprovement,
    ExpectedImprovement,
    UpperConfidenceBound,
)
from botorch.models.gp_regression import SingleTaskGP

## Mining Gold!
I used [this website](https://frnsys.com/misc/polynomial_designer/) to recreate the gold content function from the OP.

In [67]:
def gold(x: float) -> float:
    return (
        2.85
        + 9.20 * np.power(x, 1)
        + -8.32e0 * np.power(x, 2)
        + 2.39 * np.power(x, 3)
        + -2.10e-1 * np.power(x, 4)
    )

In [68]:
# Gold can occur between 0 and 6.
x = np.linspace(0, 6)
# Setup our observation features to use for model predictions.
observation_features = [
    ObservationFeatures(
        parameters={"x": i},
    )
    for i in x
]
y = [gold(i) for i in x]

Plot the gold content function over our domain.

In [69]:
render_plotly_html(
    px.line(
        pd.DataFrame({"X": x, "Gold Content": y}),
        x="X",
        y="Gold Content",
        title="Ground Truth for Gold Content",
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="6ba6ca90-8716-46b9-a4b3-a4a6d53c60b5" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("6ba6ca90-8716-46b9-a4b3-a4a6d53c60b5")) {                    Plotly.newPlot(                        "6ba6ca90-8716-46b9-a4b3-a4a6d53c60b5",                        [{"hovertemplate":"X=%{x}\u003cbr\u003eGold Content=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"","line":{"color":"#636efa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"","orientation":"v","showlegend":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"xaxis":"x","y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"Gold Content"}},"legend":{"tracegroupgap":0},"title":{"text":"Ground Truth for Gold Content"}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

## Active Learning

### Ax Helper Functions
First, define some helper functions for common Ax operations.

In [70]:
def evaluate(parameterization: TParameterization) -> TEvaluationOutcome:
    """Evaluate a parameterization on our groundtruth gold function."""
    x = cast(float, parameterization.get("x", 0.0))
    y = gold(x)
    return {"gold": (y, None)}


def create_generation_strategy(
    botorch_acqf_class, random_class=Models.SOBOL, random_trials: int = 3
) -> GenerationStrategy:
    """Strategy consisting of random search followed by surrogate/acquisition."""
    return GenerationStrategy(
        steps=[
            # Always include random steps.
            GenerationStep(
                model=random_class,
                num_trials=random_trials,
            ),
            # Combine an acquisition class with a GP surrogate function.
            GenerationStep(
                model=Models.BOTORCH_MODULAR,
                num_trials=-1,
                model_kwargs={
                    "botorch_acqf_class": botorch_acqf_class,
                    "surrogate": Surrogate(SingleTaskGP),
                },
            ),
        ]
    )


def create_client(generation_strategy: GenerationStrategy) -> AxClient:
    """Create a ax client for the gold content experiment."""
    ax_client = AxClient(
        generation_strategy=generation_strategy,
        random_seed=1,
        verbose_logging=False,
    )
    ax_client.create_experiment(
        name="gold_content",
        parameters=[
            {
                "name": "x",
                "type": "range",
                "bounds": [0.0, 6.0],
                "value_type": "float",
                "log_scale": False,
            },
        ],
        # We want to get the most gold possible.
        objectives={"gold": ObjectiveProperties(minimize=False)},
    )
    return ax_client


Cache = Tuple[Dict[int, TModelPredict], Dict[int, List[List[float]]]]


def run_ax(n: int, ax_client: AxClient, acqf_n: int = 1) -> Cache:
    """Run an ax client for a specified number of iterations."""
    predictions: Dict[int, TModelPredict] = {}
    acquisitions: Dict[int, List[List[float]]] = {}
    for i in range(n):
        # Get the next trial's parameterization.
        parameterization, trial_index = ax_client.get_next_trial()
        # Extract the model for caching this iteration.
        model = cast(
            TorchModelBridge,
            not_none(ax_client.generation_strategy.model),
        )
        # We won't always have an TorchModelBridge that supports evaluation.
        # If we do, run evaluation and cache the results for visualizing.
        try:
            predictions[i] = model.predict(
                observation_features=observation_features,
            )
            acquisitions[i] = [
                model.evaluate_acquisition_function(
                    observation_features=observation_features
                )
                for _ in range(acqf_n)
            ]
        except Exception:
            pass
        # Complete the trial by evaluating the true gold content.
        ax_client.complete_trial(
            trial_index=trial_index, raw_data=evaluate(parameterization)
        )
    return predictions, acquisitions

Store results of each optimization so we can compare the different methods at the end of this section.

In [71]:
results: Dict[str, pd.DataFrame] = {}

### Surrogate Function

Sample uniformly from the domain to show how we learn the gold content with our surrogate function. Our surrogate function will be a [Gaussian Process](https://cs229.stanford.edu/section/cs229-gaussian_processes.pdf):

$$
\begin{align*}
  \begin{bmatrix}
    f(x_1) \\
    \vdots \\
    f(x_m)
  \end{bmatrix}
  &\sim \mathcal N \big(\begin{bmatrix}
    m(x_1) \\
    \vdots \\
    m(x_m)
  \end{bmatrix}, 
  \begin{bmatrix}
    k(x_1, x_1) & \dots & k(x_1, x_m) \\
    \vdots & \ddots & \vdots \\
    k(x_m, x_1) & \dots & k(x_m, x_m)
  \end{bmatrix} \big) \\
m(x) &= \mathbb E[x] \\
k(x, x') &= \mathbb E[(x - m(x))(x' - m(x'))] \\
y^{(i)} &= f(x^{(i)}) + \epsilon^{(i)},\quad i=1,\dots,m, \quad \epsilon^{(i)}\sim N(0, \sigma^2)
\end{align*}
$$

In [72]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=ProbabilityOfImprovement,
    random_class=Models.UNIFORM,
    random_trials=5,
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)

[WARNING 08-11 09:43:17] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:17] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).


Plotly can be animated by adding a [slider](https://plotly.com/python/sliders/) to the figure layout. Note, the first couple points are the uniformly random samples. These are followed by alternating the surrogate function and a query point.

In [73]:
fig = go.Figure()
# Plot our groundtruth function for comparison.
fig.add_trace(plot_groundtruth(x=x, y=y, kwargs=get_line_kwargs()))
# Iterate through the trials.
n = len(ax_client.generation_strategy._generator_runs)
j = len(fig.data)
for i in range(n):
    # Not every iteration has predictions.
    if i in predictions:
        fig.add_trace(
            plot_predictions(x=x, predictions=predictions, i=i),
        )
    # Finally, add where we observed this iteration.
    fig.add_trace(
        plot_observed(
            ax_client=ax_client,
            gold_fn=gold,
            i=i,
            kwargs=get_scatter_kwargs(),
        )
    )
# Create the animation steps.
steps = [
    dict(
        method="update",
        label=fig.data[i].name,
        args=[
            {
                "visible": [True] * (j + i) + [False] * (len(fig.data)),
                "title": str(i),
            }
        ],
    )
    for i in range(len(fig.data))
]
# Format the layout of the plot
fig.update_yaxes(range=[1, 9])
fig.update_xaxes(range=[-1, 7])
fig.update_layout(
    title="Gold Search",
    xaxis=dict(title="X"),
    yaxis=dict(title="Gold Content"),
    # Add the animation steps onto the layout.
    sliders=[dict(active=0, steps=steps)],
)
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="748b13d1-57bb-40fd-a2fc-bdf488f12613" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("748b13d1-57bb-40fd-a2fc-bdf488f12613")) {                    Plotly.newPlot(                        "748b13d1-57bb-40fd-a2fc-bdf488f12613",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":false,"x":[0.32872711926390363],"y":[5.057664805217066],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":false,"x":[1.4348541948065263],"y":[5.091532753266253],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":false,"x":[1.1448646473418669],"y":[5.703244208949001],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[4.012995102221842],"y":[5.776814007863983],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[2.451072738768894],"y":[3.0295919107202014],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.07316634384684,4.999504522910488,5.032634654794059,5.164273638531742,5.3575527850944376,5.5568489891338,5.711965298159969,5.793407593601372,5.793046710584509,5.714025272511392,5.5600243071368824,5.337923204662083,5.070524245665279,4.788961815910491,4.509782877049986,4.231677995788834,3.9480319023640744,3.6620736253279857,3.39643006646367,3.192706536745609,3.099594778508046,3.1508663930297627,3.3459010613785805,3.6534271369530398,4.026144048242655,4.413922289654745,4.773380320739256,5.073826644284898,5.300281527146908,5.454264163752668,5.552622538439179,5.624192584556933,5.703762590807438,5.822971404330607,5.99911603888284,6.229694457181241,6.498491485685141,6.783974911678316,7.065474533162904,7.326647652755239,7.55671286607771,7.750218586592451,7.906049409724522,8.02618143070912,8.114497290043163,8.175813139212142,8.215163557391369,8.23732952209914,8.246566238545071,8.246479913608551,2.1038117576686997,2.199054270314816,2.3146515175484197,2.454304178794718,2.6219121269328403,2.821286080558268,3.0556775521343984,3.3270771103308348,3.6352434209155113,3.9764615523321556,4.342102095479228,4.717177358659123,5.079277254857443,5.398508766827107,5.639314402783944,5.765194097747739,5.747192701884677,5.576172607972804,5.273003013151644,4.881693970881187,4.454369317829374,4.039878164752305,3.6767265690557367,3.3894657457024477,3.1876287569198007,3.0666662403321716,3.010814888092022,2.998176501454861,3.0081848661092496,3.030702344003669,3.073740034884545,3.162093953009095,3.322827933956939,3.569615051916137,3.894282847692029,4.267682326786479,4.649030655275435,4.999768614540697,5.294025964716555,5.515119030153113,5.643537656434499,5.6682908988889835,5.606217448075431,5.493531441859911,5.36459781712188,5.234645610425719,5.094845010060559,4.922132176436568,4.698442022644098,4.421796493248411],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[4.194693878482701],"y":[6.431018758151026],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.011682324084294,4.967292420626053,5.025202045358007,5.167691506803046,5.35759903216066,5.547168449602896,5.694598673597294,5.773959136627116,5.775509317842225,5.699511018224228,5.550181987100491,5.3373942847125,5.082027050882892,4.808793912710115,4.531893404446643,4.253455542677204,3.971746765137313,3.6912837140884633,3.4293691920870373,3.2157764648311256,3.0846628857866976,3.060292735828231,3.1446283048135526,3.3187977990490745,3.5524082396772885,3.8134444764344906,4.076296630963971,4.326743674647874,4.563468597947743,4.796146785075203,5.0405339217118525,5.311499066013494,5.615756306118919,5.947097660441558,6.2881466518593205,6.624132963507047,6.954400881726091,7.285305283663272,7.6214249824415825,7.962303750557356,8.302792271205293,8.634917506364527,8.949959232100325,9.24008618238094,9.499354068036084,9.724112888748968,9.91297272384869,10.066494452268351,10.186747760928867,10.276840394120928,2.4965911970642187,2.813154012031427,3.16428410971422,3.5483202271228196,3.961176468593514,4.395693472714459,4.841050846766807,5.282377259414732,5.700747757610311,6.073802111417138,6.377227999976317,6.587287765666102,6.6843713658020985,6.657173596066782,6.506507431817513,6.2471257817942165,5.905170436837344,5.506829751551806,5.071205977287646,4.617833080232228,4.171542923542104,3.7606068620992783,3.4116167660073353,3.1440573572851385,2.966415397344681,2.874810571196833,2.8545611925303187,2.8846572335391953,2.944583349133419,3.022110487173903,3.119394142106782,3.2520810268354223,3.438733673862437,3.6890795552786795,3.9973051345597783,4.342174713201126,4.6932464960203255,5.020030222256385,5.29868887712577,5.510632776542448,5.63786040625332,5.671791673736523,5.624734746493644,5.523755297786458,5.396327195188752,5.257711648848211,5.105803731317368,4.925695757685748,4.701521788073669,4.4257313336465565],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[4.491198145517794],"y":[7.41938481136026],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.688935158788733,4.757263160615211,4.9151940262942935,5.134072034212077,5.374241300214174,5.593106914798788,5.756281377409039,5.842577941386738,5.842147001903871,5.751541476554139,5.5718213954975475,5.314564636658083,5.00737239981946,4.684544268081935,4.370780256336546,4.076644725009364,3.8035766609236195,3.5522523872648795,3.3294254705432156,3.149906502890123,3.032564015291765,2.9916573240373903,3.028825376678319,3.1330456504453497,3.2862045300608713,3.469976102799417,3.6716546641515455,3.887435044406619,4.122454519809857,4.3877050809853815,4.694703266390146,5.049558869425854,5.448686085515852,5.878452710084925,6.319765515819786,6.754196286926548,7.163335220172872,7.532886751931623,7.862797880872357,8.1661554444958,8.461075522557168,8.764060951480399,9.086359390352856,9.432854925393542,9.802622312785426,10.190333919155057,10.587923474378039,10.986136097637678,11.375776231328494,11.748591955594595,4.59768284060668,5.209894091630055,5.810774805544268,6.382891156057303,6.906816783258837,7.3621427802900765,7.728961711771088,7.9898044823152725,8.13189367060431,8.149409387174314,8.045256675324776,7.831632288981851,7.528656221367233,7.160756628149617,6.751172605735728,6.317848788216408,5.876645512312088,5.439517660355619,5.010475483930592,4.591987112990491,4.1915487085287735,3.8229928033293814,3.5034571857165453,3.2483785741252547,3.0668035070187454,2.9586888161259077,2.9150933476311685,2.9213679765697833,2.9626394166254744,3.030046001970331,3.125336023268469,3.259945114954613,3.4468845744693204,3.691967901689031,3.9892409555014274,4.321889365645164,4.667455647787947,5.003948810056101,5.311901565631748,5.569224984381501,5.747870468067624,5.825894449897707,5.802356667900556,5.695999817585351,5.534406224061591,5.341540169415405,5.129189423455499,4.895517371157193,4.630674455417304,4.324414590323383],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.608163665936905],"y":[7.746444938096204],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.575519201693577,4.699806649386003,4.896328546588739,5.136835688306437,5.385773660386025,5.606425046981714,5.7689602366772075,5.853946860038738,5.851156268240532,5.756645032505787,5.572493884077128,5.311997802970214,5.002473230806389,4.67617354546572,4.357154443142613,4.057822317331819,3.782586648183381,3.534040272174998,3.3181571808604344,3.1460216601573534,3.0312398995763146,2.9840215257076594,3.0056842698339796,3.0885854992390094,3.220056788124329,3.387377482180945,3.5819741546033828,3.8016384897876683,4.050228121852698,4.335009305574577,4.662472288201293,5.034037006739993,5.443415333198203,5.8771659540134555,6.318600859707222,6.75196570878708,7.161756942537717,7.534305503211123,7.860976562683477,8.141838219282375,8.387129935215114,8.613459387302207,8.838916274194304,9.0792567892431,9.345706313713913,9.644210060570536,9.975718374923915,10.337079607800096,10.722193280060106,11.12317993510144,5.935293020410067,6.520710120715554,7.0549996632607055,7.522193708343121,7.907475932189097,8.198497713938556,8.386758622939968,8.468832242469528,8.447120651453567,8.329748501336947,8.129230459099285,7.859799820448051,7.53401952143703,7.161142056785434,6.751374173881461,6.318215875875912,5.876822186256043,5.4405752735292,5.016216468019225,4.6074962895502765,4.220576348127558,3.865906800226299,3.5566186817383874,3.3050120575533417,3.1189398254305107,2.9995282631109097,2.9410792640093435,2.933318250987459,2.965448535463811,3.0307917913356035,3.130186480406596,3.2713252402945034,3.462844067733325,3.7078649057968507,4.000554035137165,4.3266393852185585,4.666983811522136,5.001656137906867,5.31093830175758,5.571525297354402,5.75568147790567,5.842191433453518,5.828216916822813,5.728212769978933,5.565623985989545,5.363000540930447,5.134494173767781,4.883303413258469,4.604525192950797,4.290545060042975],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[4.699603014745402],"y":[7.964008751168905],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.554023286522054,4.6894248140034165,4.893371282488958,5.137844228155514,5.3881694273653435,5.608794782911614,5.770798868873624,5.85516432778863,5.851724952661134,5.756591964706958,5.572116195742437,5.311838811326354,5.002819296471501,4.676700681543766,4.357240361677949,4.057089882233097,3.7812081005024885,3.5326311538921042,3.317345668051653,3.145945154634501,3.0312714021522855,2.982958143090487,3.0023474672819073,3.0823968463139284,3.211306960327825,3.377147114821844,3.5717817493399875,3.792956274087117,4.0440306071095655,4.331506000414363,4.661125523639355,5.033875420737961,5.443528141051006,5.877137796448127,6.318610591196382,6.752408445607565,7.162662276861828,7.534546574258889,7.856879717904279,8.125702356901952,8.347877643233026,8.538428281527253,8.716348693460956,8.90043264998519,9.106212641065138,9.344322948960112,9.620083328812274,9.933935446416715,10.2823681088751,10.659039320328425,6.27844642083621,6.838197908976841,7.336492952235262,7.759293069005221,8.094721105632107,8.334279974014873,8.473935933703496,8.51479308851488,8.463018314518528,8.328677483379202,8.12331532253288,7.85663581216383,7.534243818020564,7.162087169947465,6.751797281449238,6.31819317767644,5.876761999238586,5.440646239867888,5.016658710756508,4.608847577000458,4.223462513482099,3.8706690243188526,3.563045284099769,3.312311428522833,3.125961577281321,3.005146496582162,2.9445998096114625,2.9347580880257307,2.965560233125756,3.0307735266085873,3.1311365710383186,3.273708665000218,3.4663398951172533,3.7116355303301907,4.003727652102242,4.328728559845956,4.668015928850581,5.0019620438802255,5.310807871940873,5.571166350775728,5.755595712473674,5.843236506809652,5.831022433483485,5.732600662125818,5.570491618065869,5.366717266061792,5.135570497466749,4.880951181295884,4.598784924678657,4.281999099036873],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[4.790397405221612],"y":[8.139446456560734],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"yaxis":{"range":[1,9],"title":{"text":"Gold Content"}},"xaxis":{"range":[-1,7],"title":{"text":"X"}},"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"Ground Truth (f)","method":"update"},{"args":[{"visible":[true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"1"}],"label":"i=1","method":"update"},{"args":[{"visible":[true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"2"}],"label":"i=2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"3"}],"label":"i=3","method":"update"},{"args":[{"visible":[true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i=4","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"5"}],"label":"i=5","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"6"}],"label":"p=6","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i=6","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"8"}],"label":"p=7","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"9"}],"label":"i=7","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"p=8","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"11"}],"label":"i=8","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"12"}],"label":"p=9","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i=9","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"14"}],"label":"p=10","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"15"}],"label":"i=10","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Cross Validation

In [74]:
# Extract the final model
model = cast(
    TorchModelBridge,
    not_none(ax_client.generation_strategy.model),
)
# Perform cross validation to estimate out of sample error.
cv = cross_validate(model)
diagnostics = compute_diagnostics(cv)
print_markdown(pd.DataFrame(diagnostics).to_markdown())

|      |   Mean prediction CI |      MAPE |     wMAPE |   Total raw effect |   Correlation coefficient |   Rank correlation |   Fisher exact test p |   Log likelihood |      MSE |
|:-----|---------------------:|----------:|----------:|-------------------:|--------------------------:|-------------------:|----------------------:|-----------------:|---------:|
| gold |             0.239113 | 0.0495505 | 0.0414965 |            1.62874 |                  0.938666 |           0.833333 |              0.166667 |          8.39369 | 0.293955 |

In [75]:
fig = interact_cross_validation_plotly(cv)
fig.update_layout(dict(width=None))
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="89e130c3-ab9b-4ee8-b4aa-9036d6bb011c" class="plotly-graph-div" style="height:500px; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("89e130c3-ab9b-4ee8-b4aa-9036d6bb011c")) {                    Plotly.newPlot(                        "89e130c3-ab9b-4ee8-b4aa-9036d6bb011c",                        [{"hoverinfo":"none","line":{"color":"black","dash":"dot","width":2},"mode":"lines","showlegend":false,"visible":true,"x":[1.2709608779420252,8.770881714793267],"y":[1.2709608779420252,8.770881714793267],"type":"scatter"},{"error_x":{"array":[null,null,null,null,null,null,null,null,null],"color":"rgba(128,177,211,0.4)","type":"data"},"error_y":{"array":[1.8015391468374415,0.44462340504182923,0.4334904838895837,0.16954053183056034,1.4921744775166508,0.08763873122603702,0.05039194661615546,0.030598320552780223,0.08143566735225702],"color":"rgba(128,177,211,0.4)","type":"data"},"hoverinfo":"text","marker":{"color":"rgba(128,177,211,1)"},"mode":"markers","name":"In-sample","showlegend":true,"text":["\u003cb\u003eArm 0_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.058 [nan, nan]\u003cbr\u003ePredicted Outcome: 6.628 [4.827, 8.430]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 0.32872711926390363","\u003cb\u003eArm 1_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.092 [nan, nan]\u003cbr\u003ePredicted Outcome: 5.347 [4.903, 5.792]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 1.4348541948065263","\u003cb\u003eArm 2_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.703 [nan, nan]\u003cbr\u003ePredicted Outcome: 5.376 [4.942, 5.809]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 1.1448646473418669","\u003cb\u003eArm 3_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.777 [nan, nan]\u003cbr\u003ePredicted Outcome: 5.786 [5.616, 5.955]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.012995102221842","\u003cb\u003eArm 4_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 3.03 [nan, nan]\u003cbr\u003ePredicted Outcome: 3.104 [1.612, 4.596]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 2.451072738768894","\u003cb\u003eArm 5_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 6.431 [nan, nan]\u003cbr\u003ePredicted Outcome: 6.432 [6.344, 6.519]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.194693878482701","\u003cb\u003eArm 6_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 7.419 [nan, nan]\u003cbr\u003ePredicted Outcome: 7.42 [7.370, 7.471]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.491198145517794","\u003cb\u003eArm 7_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 7.746 [nan, nan]\u003cbr\u003ePredicted Outcome: 7.743 [7.713, 7.774]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.608163665936905","\u003cb\u003eArm 8_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 7.964 [nan, nan]\u003cbr\u003ePredicted Outcome: 7.972 [7.890, 8.053]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.699603014745402"],"visible":true,"x":[5.057664805217066,5.091532753266253,5.703244208949001,5.776814007863983,3.0295919107202014,6.431018758151026,7.41938481136026,7.746444938096204,7.964008751168905],"y":[6.6284370753716795,5.347301959124916,5.375900057595387,5.7858828106524465,3.1040408480428234,6.4315461328688,7.42024850247203,7.74319107980205,7.971890591826844],"type":"scatter"}],                        {"annotations":[{"showarrow":false,"text":"Show CI","x":1.125,"xanchor":"left","xref":"paper","y":0.9,"yanchor":"middle","yref":"paper"}],"height":500,"hovermode":"closest","showlegend":false,"updatemenus":[{"buttons":[{"args":[{"visible":[true,true]},{"xaxis.range":[1.2709608779420252,8.770881714793267],"yaxis.range":[1.2709608779420252,8.770881714793267]}],"label":"gold","method":"update"}],"x":0,"xanchor":"left","y":1.125,"yanchor":"top"},{"buttons":[{"args":[{"error_x.width":4,"error_x.thickness":2,"error_y.width":4,"error_y.thickness":2}],"label":"Yes","method":"restyle"},{"args":[{"error_x.width":0,"error_x.thickness":0,"error_y.width":0,"error_y.thickness":0}],"label":"No","method":"restyle"}],"x":1.125,"xanchor":"left","y":0.8,"yanchor":"middle"}],"xaxis":{"linecolor":"black","linewidth":0.5,"mirror":true,"range":[1.2709608779420252,8.770881714793267],"title":{"text":"Actual Outcome"},"zeroline":false},"yaxis":{"linecolor":"black","linewidth":0.5,"mirror":true,"range":[1.2709608779420252,8.770881714793267],"title":{"text":"Predicted Outcome"},"zeroline":false},"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"margin":{"b":90},"title":{"text":"Cross-validation"}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

## Bayesian Optimization

### Probability of Improvement (PI)
Choose next point based off the highest probability over the current max.


$$
\begin{align*}
x_{t+1} &= \arg\max_x P(f(x) \geq (f(x^+))) \\
& = \arg\max_x \Phi\big ( \frac{\mu_t(x) - f(x^+)}{\sigma_t(x)} \big )
\end{align*}
$$

In [76]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=ProbabilityOfImprovement
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)
results["PI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:18] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:18] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 09:43:19] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [77]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="d766d664-db7c-4c74-98c5-bba399e87f60" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("d766d664-db7c-4c74-98c5-bba399e87f60")) {                    Plotly.newPlot(                        "d766d664-db7c-4c74-98c5-bba399e87f60",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.04806715789974354,0.038950223365649135,0.030354336396250188,0.022509385582449165,0.01565484471444161,0.010008710974654726,0.005719485323507537,0.0028074414473676745,0.0011187110567908807,0.00033445474097389756,6.763593052259173e-05,8.266832959809783e-06,5.831695418172122e-07,2.985012540800117e-08,2.491202025783452e-09,1.1707468232903512e-09,5.124717396995852e-09,8.585568213060402e-08,1.659421144300826e-06,2.0170013641916788e-05,0.0001388493685416449,0.0005912252445761788,0.0017531414190953476,0.0039971044449773774,0.007537595566893882,0.012382573513050206,0.018389243070984225,0.02537329167205872,0.033241721103364125,0.04215696674967249,0.05276737552157317,0.06653361719863721,0.08605825133743371,0.11490525041123252,0.1558616533909716,0.20776285815694495,0.26457331412072066,0.3189376814982125,0.366019099282582,0.40418801632713064,0.43375533297023466,0.4556737048276599,0.4707950554849367,0.479576388530276,0.4821189283174623,0.4785898253655618,0.46994527950710946,0.4582178737478434,0.44568195167095287,0.4338066248492031],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[5.376579210943656],"y":[7.78026814236398],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.03270227567121766,0.02699984846732462,0.021605335096855312,0.016645775335546786,0.01224713736324175,0.008519159826573702,0.005535693919053022,0.003314228817432878,0.0018021351608542668,0.0008794277365751368,0.00038397629851540864,0.00015265943848391807,5.8378307113452185e-05,2.388250209303332e-05,1.2153796514674943e-05,8.90432277240389e-06,1.0011264030674819e-05,1.629988932331542e-05,3.346074355703932e-05,7.492737417722573e-05,0.000164820796343754,0.0003363574213714318,0.0006229168460518576,0.0010450875170578175,0.0016011853600457527,0.002266640928120571,0.0030023685229162646,0.0037686228199229313,0.004540322979693665,0.005321129056209206,0.006155246125739249,0.00713721089258916,0.008419872293406717,0.010217038120916306,0.012786108561788233,0.016363692147031886,0.021057945463689984,0.02674066846041739,0.03299832108694814,0.039201945586391396,0.044701388848710284,0.049093623527079105,0.05248475809260955,0.05563412203312857,0.05983911035537887,0.06648225453615765,0.07638454912165019,0.08933423717327743,0.10416035012235633,0.11935167318622429],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[7.495651257760675,7.284834873266803,7.066648672973573,6.843106579207252,6.616719721149,6.390513858849745,6.168023792794874,5.953256833214429,5.750616697632555,5.564779038074719,5.400510484652241,5.262425011981605,5.154675016004324,5.080580144516059,5.0422049366001085,5.039906630651957,5.071909162410016,5.134264322955848,5.221450663302278,5.327092357566368,5.444597336589617,5.567694335321278,5.69085997443865,5.80963297282226,5.920816446145916,6.022571306179688,6.114404639850731,6.197057358718479,6.272296172046842,6.342616873323181,6.410869842905653,6.479825268191519,6.551705345010836,6.627723635688087,6.707687178174618,6.789787685359177,6.870937771331512,6.947534691565976,7.0162211970593304,7.074519720757224,7.121287600760339,7.156963394743796,7.183594938519506,7.2046588613056555,7.224699072361968,7.248825258084782,7.282077289406204,7.328642314700801,7.391199689415242,7.4708353553172735,6.244371433637564,6.380361619600279,6.4857553812090085,6.558925988108057,6.599590092991258,6.608925920272547,6.5895898562198,6.545575313341296,6.481545809613815,6.402025221171347,6.310774782550063,6.210403359288035,6.1022279125734675,5.986384732490723,5.8621741298915735,5.728601597092776,5.5850568085970735,5.43200750549391,5.271317815118637,5.106074215983993,4.940227463057346,4.778168188253633,4.624291483562842,4.482590301250648,4.356304463717433,4.247642149406956,4.157583920461708,4.085775199382301,4.030510869208282,3.9888145543540365,3.9566143039828385,3.9290150310244236,3.9006654014728843,3.8662122993906496,3.8208291753302377,3.7607934114317016,3.68396730695931,3.589827927557511,3.4791971757993863,3.353918972676915,3.216537498561446,3.070003181522298,2.917421925272162,2.7618543050479074,2.60616517081994,2.452919983933062,2.304321847045188,2.1621821280418287,2.027917433249126,1.902566130487723],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[6.0],"y":[2.6100000000000705],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.08653692470322279,0.08156056891101435,0.07625600182025259,0.07065389706779239,0.06480464613287185,0.0587824508630282,0.05268861264445879,0.04665279448677954,0.04083065378889843,0.03539627440546545,0.03052878913022684,0.026394888010511496,0.023132125566322995,0.020840002602230068,0.019583400019066766,0.019404299698161744,0.020327254734751176,0.02235412696439887,0.025455591003541878,0.029553476554349194,0.034507519618515815,0.040118901403697116,0.04614988225923302,0.05235081942124289,0.05848558461157401,0.06435048346958634,0.06978598681967643,0.07468283604617043,0.07898427535806345,0.08268491609948829,0.08582466436187419,0.08847384204779118,0.09070411766668868,0.09254093313601472,0.09389891475116421,0.09451989938665824,0.09397788859387556,0.09176573020313501,0.08741953273970508,0.08066118295517602,0.07154360270953186,0.06056901643391124,0.048715657369874474,0.03728086441426747,0.02750731428417421,0.02015074518290084,0.015299190652774032,0.012574766288612716,0.011489487218403602,0.011674051234425921],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[10.101835960966621,9.888198543890951,9.658238360386132,9.413302160952702,9.155530794462443,8.887974501659706,8.614685118088907,8.340767220703402,8.072365901422021,7.816564956560724,7.581166724830069,7.374324846263104,7.204005499591133,7.077263151984627,6.999335443308955,6.972589683391676,6.995440643965557,7.062060768490481,7.1634897961014286,7.289016474941914,7.427384067775535,7.567778983479824,7.700595295745157,7.817984728305926,7.914209922374786,7.985820110038006,8.031664922398372,8.052756291079934,8.051982554324107,8.033675252211943,8.003030056982594,7.965391271459723,7.925426649291417,7.886247531698084,7.848568726133738,7.810169967018549,7.766448613141656,7.711849341365584,7.641270062929096,7.551206099982584,7.440549475902452,7.311004421531266,7.167118419863434,7.015963409686333,6.866537131647981,6.728990922048703,6.613818246371373,6.531031681013244,6.489307994101274,6.495224227837332,3.815503019839656,4.0809396964228135,4.304558188312066,4.482725761700065,4.6138023051215145,4.69871999165364,4.741075711789359,4.7468742272226665,4.723370563258119,4.677625501050517,4.615369116335052,4.5402741587391775,4.453684452510247,4.354813161767793,4.2413946899107575,4.110739339958814,3.961098652757516,3.7930898458419375,3.6102244965341526,3.4183176537896034,3.2246115332378413,3.036878561704627,2.8625930748560178,2.708222418217258,2.5786606598239565,2.476811301509039,2.403317709886214,2.356439183734948,2.3320742021732315,2.32393809210235,2.3239078118235215,2.322549462152106,2.3098421621876515,2.276102815258609,2.213098356695345,2.115298577007507,1.980875611665316,1.8114876852392126,1.6113535627061921,1.3863243960311729,1.1430722616705222,0.8884345636341697,0.628924339739577,0.3703968690397721,0.11785164114969238,-0.12465624018448196,-0.3540217596326851,-0.5680372487365588,-0.76530213301512,-0.9451120541456515],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[4.298252484395651],"y":[6.794103154945049],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.08966711190983648,0.0842240898112912,0.07825853154207962,0.07177966454016985,0.06482502050886371,0.057471192200251174,0.04984554335982533,0.04213629767798683,0.03459592091769693,0.027529941445981625,0.021262858109987817,0.01607959916941694,0.012159259025743625,0.00953995465955167,0.008152871830216972,0.007918771523477896,0.008839496903553465,0.011015960964133287,0.014578439364465956,0.019561140321556557,0.025811943807240504,0.032994106460401525,0.040659041214327014,0.04833394718545018,0.055585606056830994,0.06205265534159303,0.06745679517776089,0.07160790895689552,0.07441660938663533,0.07592502427606128,0.07636223734110324,0.07621890092762741,0.07630586653781592,0.07770768284392211,0.08148684044486078,0.08805973531424963,0.09656662879266104,0.10478354100566839,0.10982047848773038,0.10913104532755497,0.10126638168116592,0.08634064086687995,0.06635092503035518,0.045083942060355674,0.0269096841154058,0.014535677176743566,0.007746027514372361,0.004623898782483069,0.0034354351972235566,0.0032671894432677135],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[10.359563100177485,10.127498033751957,9.869344942840137,9.585324437239965,9.276787700662512,8.946513041659006,8.599000469567262,8.240730341349234,7.8803377118391955,7.528638211620608,7.198426139270717,6.903954599409793,6.660006520389638,6.480481930894404,6.376470129328743,6.353853621898401,6.410725134348763,6.536579382788979,6.714734303173941,6.925328685900739,7.147836799271177,7.363026640280124,7.554386998026512,7.7090932524243625,7.818595449166712,7.878902850195951,7.890615194159141,7.858719575410986,7.792139495798914,7.702995435984315,7.605521195333904,7.514585763715643,7.443806724663824,7.403318389337388,7.397383122698253,7.422426568058149,7.467116795663586,7.51458311380571,7.54606007108933,7.544655547871142,7.4982472083196905,7.401257324841062,7.255257660480019,7.068510485358868,6.854702789775962,6.631279530868436,6.417798762565178,6.2343236439524095,6.099718106292093,6.029899921350274,3.84371956224354,4.220445870713744,4.552034818879386,4.832622361275633,5.058917118936161,5.231691829150014,5.356270455073464,5.442191355741292,5.500592805710253,5.5408318477811465,5.567916775337429,5.581126012907654,5.573993431210562,5.535708846895811,5.453844626170821,5.318117421568003,5.123909996012092,4.873960345330927,4.57809652206335,4.251272874138155,3.9112510570126013,3.576450281151235,3.2641486951690046,2.989094362389832,2.762508161283289,2.5914253600409713,2.4783173897096704,2.4209503871583404,2.4124639050219296,2.44168481732228,2.493721681855289,2.550907271036703,2.594164317608307,2.604853306096338,2.567113089318842,2.4706051044974533,2.3127094092004232,2.0978559072765672,1.8352404096721253,1.5366565191912565,1.214727978718305,0.8816049333962352,0.5481056658823338,0.22323921050011553,-0.08597458769778488,-0.3744718152207849,-0.638972847083898,-0.8777331072926522,-1.0902620803742984,-1.2770426796645715],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[4.702762526338227],"y":[7.97083381305886],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.15521959126548893,0.15300862259666823,0.1498826857563066,0.1455675425534418,0.13971873073080796,0.13190784693637497,0.1216136605503268,0.10823421265700107,0.09116477917877698,0.07006016762213087,0.04556540246919751,0.020980694301082417,0.004047759051219702,3.605164637933026e-05,4.1567441753608643e-17,1.0593636629076215e-98,6.660105530183806e-10,0.00023876872362523017,0.0055125785760729825,0.01914927513793499,0.03524630973460835,0.048846504410500015,0.05798188133899445,0.06222820190091103,0.061730239720895516,0.056823128632072076,0.047987480091922316,0.036028498241639076,0.022468365445896678,0.010020481326018146,0.002211174097759848,8.154814061963776e-05,8.094382155404229e-09,1.0184514870575887e-23,2.0735509286007857e-43,8.201398951485256e-20,8.181237148992037e-07,0.006622890189304626,0.22018749303211074,0.7766985776605184,0.8719450775495452,0.8828395506071974,0.8747505088602466,0.7675836036468769,0.07706053288242017,8.632509787514815e-10,5.5063984338751604e-31,2.3751138495285948e-58,1.0399303993859618e-129,1.2320065118431594e-270],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[21.676767258261275,21.13005010660933,20.454106138339977,19.630228382844418,18.64188555062205,17.477365970523742,16.13325566358391,14.618691472232442,12.960115697139818,11.205929377755103,9.429988090309912,7.732334911334418,6.235019858489645,5.070530931631973,4.360634453255586,4.1848129200711845,4.542246634697611,5.338225903338655,6.417702143666762,7.605027521121874,8.733373261191389,9.663690634564004,10.295251260791769,10.570328353161335,10.475208035048325,10.038880107409607,9.32975099367756,8.449759413513647,7.5245633818101565,6.688294829562247,6.0621854960281745,5.728730527976311,5.707443981439658,5.944233517399304,6.330578464923357,6.761760686418145,7.185747196804042,7.5652248362256325,7.878459749674508,8.141286956072545,8.34975529575322,8.449524112601505,8.391164171796682,8.16947882569555,7.79040776259195,7.212189738273538,6.372883189533406,5.2755655560944,3.994941501785359,2.6816171467164875,2.635883356614943,3.9402241307523242,5.218037056351114,6.333415035215678,7.179042556707615,7.750958576386673,8.080508893850348,8.220960904628257,8.24771616703707,8.204341616494432,8.075807039953354,7.8345431375730294,7.5030683035955485,7.128094420820124,6.724842433250822,6.301676422582003,5.8580666113226805,5.330618521492264,4.633876754104501,3.723138711398944,2.6185036646415423,1.3976413945911466,0.17385906593975609,-0.9282046384865223,-1.7929809124448939,-2.328636776283364,-2.4765803064566168,-2.21721804369158,-1.5732264381658414,-0.6109006851940366,0.5608111213768452,1.7949866594156485,2.917364337528333,3.745562760553157,4.119007994667209,3.939537525191551,3.20578035555236,1.9990126284722205,0.4440267413489343,-1.3231968477269893,-3.1771229122116917,-5.014504098519572,-6.758701335648006,-8.359003679809714,-9.787130980745115,-11.032547218916012,-12.09765581224364,-12.993489720176054,-13.73617619609674,-14.344239036888343],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[5.0411465101047845],"y":[8.353438586358578],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.14057140027303994,0.13779745226525306,0.13394958665715567,0.12875386869528815,0.12188055708770378,0.11294280637673919,0.10151172627208697,0.08717429285343327,0.06969537747152607,0.04941381731652445,0.028077875122818143,0.010018639905387074,0.0010799011751257339,1.461023140568827e-06,3.938663948735982e-25,1.824e-320,5.103269968946312e-14,1.09794504426673e-05,0.0009774289352789192,0.005572545047319623,0.012811663668895416,0.019640774003510966,0.024054633788159533,0.02530571018127387,0.023439502541747315,0.019013694270409588,0.013031669420115957,0.006940352120025311,0.002392738093842317,0.00034754164901230385,6.5544696450423385e-06,2.653698870018376e-10,1.7389607944820187e-26,3.3637362315297265e-136,1.9170174956089534e-308,2.1543128149450002e-163,7.083475480745266e-48,3.8960315423158356e-19,8.413894836327964e-14,0.0001807590842291199,0.18418313013499454,0.4792249577501559,0.19743594053581043,0.00023752901322700732,8.238590173674814e-25,4.598522789451187e-79,1.938902660200601e-232,3.575330419809842e-243,0.0,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[25.259279637305617,24.2681398955971,23.118464028451026,21.802684282482122,20.319254682963336,18.675025873461315,16.887824747587743,14.989001780088284,13.025563857912767,11.061336790680393,9.17641797061728,7.464024816426813,6.023786908829072,4.950673566473523,4.31923262351829,4.163786293447482,4.457720120933229,5.108981231019396,5.983172272290577,6.931036097174712,7.810910445883848,8.50534819462837,8.932144909477003,9.050404322515584,8.86227104515902,8.410729183003497,7.773568477696699,7.053417225647296,6.363803289167308,5.811715285562368,5.478272799007309,5.400962112097046,5.563228180124054,5.899027916899841,6.318518553035727,6.751329795548127,7.168274448742352,7.545511658824005,7.8640576477575825,8.119158692218882,8.290639073596079,8.35396148584117,8.298654724510103,8.107304650335665,7.7591753513505175,7.214682387509611,6.409812943794079,5.327816941531594,4.025772663152058,2.6254831684652546,2.617738078973122,4.00699498456494,5.311196762498126,6.402647254495368,7.207288472872945,7.752332361193847,8.096960851721862,8.288804707628882,8.34658966562037,8.279001222379737,8.110196250024686,7.855081274174915,7.528541272154949,7.154740007501571,6.744368657424349,6.3126195368593105,5.8792991310013685,5.416888356029184,4.862647479487956,4.164818040654351,3.312107942227911,2.341055428180844,1.327667643598471,0.3711213658660828,-0.4245406220638239,-0.9671490046362785,-1.1898857773858427,-1.0609570766533993,-0.5894406236811682,0.17264268835616825,1.1321820576524786,2.1612008492325123,3.1081318329227074,3.814833031691772,4.139657093627043,3.9858481343990495,3.325456268954638,2.1942997792450023,0.6701390905295477,-1.1479563269855015,-3.1559356202026096,-5.256212699744948,-7.364608106503526,-9.413634828089926,-11.35311009605179,-13.149009757447564,-14.78132108551292,-16.241461704932835,-17.529655301656096,-18.65250714228062],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.026932150430952],"y":[8.353817966113354],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.14154904985138048,0.1387805059353558,0.13491701613960883,0.12968129797321126,0.12273972915011931,0.11370117817242796,0.10213272109122597,0.08761951436868819,0.06993173615673892,0.049431358541478565,0.027925149965326294,0.009839116734003443,0.0010251919035459474,1.2084589100990427e-06,4.9854972494630023e-26,0.0,1.8523331101717738e-14,8.011076712266022e-06,0.0008064988933324129,0.004789533037761709,0.011172987120841619,0.01715872423734896,0.020865915582596532,0.02161293759300807,0.019509752890095024,0.015196671980499855,0.009761917955149019,0.0046616624089942955,0.0013154684464908653,0.00012568862710041575,8.150162093848098e-07,7.717128103609637e-13,1.592749164451241e-39,0.0,0.0,0.0,1.6168730012706332e-112,1.4676031889494119e-33,6.037740554410893e-54,6.894643974407606e-11,0.09624154143378379,0.5077161454343713,0.06882114071635284,1.478039220273286e-09,9.38931942743258e-204,4.456855037948351e-208,0.0,0.0,0.0,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[26.01604592381915,24.931670154468566,23.685050425374754,22.27088960136458,20.6904234110325,18.953691970488812,17.081927940727645,15.109812461865243,13.087217578411053,11.079901525238697,9.168470417223904,7.4448042854301795,6.0051297924255,4.9390987310061405,4.314718639941113,4.159897681198105,4.443641056615254,5.072686567949753,5.913835602330264,6.820407763673872,7.6540572004652345,8.301094222784316,8.683398472838565,8.764378471237976,8.5504619642585,8.088434478233165,7.458730745441389,6.764678348163916,6.117855537812858,5.620322142159742,5.345656794922937,5.322513320513885,5.526490976760355,5.8874125030153515,6.316888356463582,6.750541045079652,7.1650624360686725,7.53986006963215,7.858583968129062,8.117462983162792,8.292452851195844,8.35435006880882,8.29110322842802,8.091031665659767,7.744444377362302,7.214781784171525,6.426424003565192,5.3507111618180785,4.039904947946278,2.6116927830252403,2.610903852194673,4.027920671093662,5.342866753003391,6.425649615478315,7.212032799507926,7.743641562282208,8.087049736455814,8.28731553422435,8.35387935191834,8.287666131675245,8.114719136355259,7.856512316944115,7.530577519016996,7.159458829672482,6.749736569429556,6.3150887702727365,5.881522933057022,5.430164690028635,4.902161599192713,4.243510759516059,3.436459058569074,2.509647580682308,1.5320898581065139,0.5982548529613156,-0.18981114306208235,-0.7395004805038039,-0.9817766524695966,-0.8815928993398185,-0.44437524718827115,0.2814814655107165,1.2062575107090292,2.2050576017762102,3.129001507744449,3.82196945340087,4.143058740415807,3.9939713209994703,3.342176551335903,2.217006373887889,0.6897208392268768,-1.145796759043133,-3.1886976740436825,-5.342483902797718,-7.522188223753985,-9.658098361264791,-11.696872716857126,-13.60087205068788,-15.346410157401827,-16.921469352515082,-18.32327088455077,-19.555955416217756],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[5.022322927162973],"y":[8.353582242638396],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false],"title":"16"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false],"title":"19"}],"label":"i = 6","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true],"title":"22"}],"label":"i = 7","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Expected Improvement (EI)
Choose the next point that has the highest expected improvement over the current max.

$$
\begin{align*}
x_{t+1} &= \arg\max_x \mathbb E[\max\{0, h_{t+1}(x) - f(x^+)\}] \\
&= (\mu_t(x) - f(x^+))\Phi(Z) + \sigma_t(x)\phi(Z) \\ 
Z &= \frac{\mu_t(x) - f(x^+)}{\sigma_t(x)}
\end{align*}
$$

In [78]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=ExpectedImprovement,
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)
results["EI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:19] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:19] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 09:43:21] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [79]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="923367d2-9a1f-451a-b866-ac86a9be1aad" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("923367d2-9a1f-451a-b866-ac86a9be1aad")) {                    Plotly.newPlot(                        "923367d2-9a1f-451a-b866-ac86a9be1aad",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.020387547294865707,0.015366768246353711,0.011042261234807756,0.007475513868284752,0.004692700060572605,0.0026729556257204003,0.0013407389506664192,0.0005679654410395972,0.000191652296832379,4.752959392155687e-05,7.808256260199064e-06,7.616091964912769e-07,4.255818513706739e-08,1.753443162904469e-09,1.2453468890936949e-10,5.4997700724870385e-11,2.537398675255238e-10,4.887853162516092e-09,1.131736462003843e-07,1.6558174847095385e-06,1.3513995542381337e-05,6.66243450772157e-05,0.0002228079363727343,0.0005581265389956207,0.0011277791080561098,0.0019389466244205227,0.002947960178436996,0.004080876173158875,0.005269082796720898,0.006493205253905086,0.007834111184501695,0.009536017602725417,0.01208680247897304,0.01628527096024659,0.023143965337439544,0.03339436352522444,0.04680085581598082,0.06201065612262954,0.07711786374848693,0.09035715099549944,0.10049069960765333,0.1069162555707797,0.10966655075737554,0.10940319013884739,0.10740742906764404,0.10546089214024584,0.10543677634159627,0.10860927306421563,0.11518377666651884,0.12451909201655227],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[6.0],"y":[2.6100000000000705],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.09547155548148073,0.09012315367766023,0.08453948709746592,0.0787720664398825,0.0728881073413244,0.06697131832618429,0.06112171615641685,0.055454102773951235,0.05009491192355703,0.04517736368719812,0.04083529291677101,0.037196584830153166,0.034377586739854055,0.03247961967305596,0.03158713259346367,0.031763954144298466,0.033041616130494215,0.03540611640048351,0.038794872713660465,0.043093464203219016,0.04813429950004522,0.05370241453782443,0.05954889924604401,0.06540920317770327,0.07102273976886013,0.07615099584494331,0.08059256879159914,0.08419441901129032,0.08685889241837394,0.08854583946417775,0.08926872452821076,0.0890834100755615,0.08806885906321629,0.08630084524699297,0.08382299663181395,0.08062595053736829,0.07665853287522406,0.07186878513802215,0.06624980256540197,0.059877598921278995,0.05293279281664019,0.04570038845225446,0.03854433060017129,0.031857471444034065,0.025995162876749578,0.0212112005623313,0.017621453620349697,0.015212767362008174,0.013892070981472354,0.013547350311460243],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[8.468340204355687,8.319943402601783,8.162103186435765,7.995976068123989,7.823209376135191,7.645993524155708,7.467096662943996,7.289871876069473,7.118225242618438,6.9565316542639515,6.809484676401886,6.681867568229242,6.578235548940744,6.502505318316022,6.45745742886477,6.444170668648828,6.46145175268706,6.50569541071989,6.571495854392652,6.652408258291769,6.741622037602594,6.832523214153313,6.919139358810739,6.996468946138988,7.060701564171072,7.109336896755312,7.141209674344048,7.156425913745337,7.15621380429822,7.142691623430785,7.118556170748796,7.08669948415421,7.049770027996924,7.009707752544808,6.967300495386683,6.921885338350014,6.871562949633711,6.813846969790884,6.746346899355913,6.667371194662391,6.576404009663911,6.474425803939747,6.364060807091803,6.249544059739751,6.1365090223222944,6.031605268918414,5.941965861532494,5.874557492559809,5.835499974628444,5.8294539833374905,3.2724665946977454,3.4182967608792794,3.538823744584498,3.6342758575024776,3.706475543289276,3.7587991609158076,3.7955038902761644,3.820904419579552,3.838698211626939,3.8514758746081603,3.8604331269947023,3.865292100258253,3.864432497103712,3.855226161379832,3.8345602474380462,3.799522864928596,3.7482098110946405,3.680520197123244,3.5983718296197003,3.5052437617572867,3.40558711057715,3.304251191484301,3.205964912551628,3.1148964345447103,3.0343019525139363,2.966266870760491,2.911539022681024,2.869452968801623,2.8379457197751607,2.813666396287744,2.7921842861264805,2.768300427512023,2.736466194054345,2.6913074394014487,2.6282439610554027,2.5441780047790177,2.438045091795591,2.310720828619293,2.164546499486759,2.0028420939693357,1.8294693544129985,1.6484675080219744,1.4637701617226218,1.2790017289428839,1.0973454043894808,0.9214713725059718,0.7535128138303064,0.5950776265320101,0.44728501457652126,0.3108177663392855],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[0.0],"y":[2.85],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0016156939514402062,0.0015020946828143617,0.001476951285408289,0.0015261094636664536,0.0016397834433463313,0.0018107938998608054,0.0020334092156318842,0.002303322538474272,0.0026188714192503016,0.0029832847700624002,0.003407562652365493,0.0039135711677260755,0.004536976148070978,0.005329536910577491,0.00635976697582091,0.007709885013455654,0.009465899789841742,0.011701760416568964,0.014464087284184355,0.017758950990433092,0.021543474585033837,0.025724982399300517,0.030167932034265366,0.03470668872617749,0.03916124552260405,0.04335319684833069,0.047120052266985284,0.05032675521508602,0.05287373880842449,0.054700971316898314,0.05578737362876173,0.05614501115902364,0.0558079218180883,0.05481663709245247,0.053201399240772815,0.05097072897762422,0.048119125606985856,0.044652202438302514,0.04061391979588341,0.03610716607905464,0.031301628871729506,0.026425029072346187,0.02173672612183378,0.017487234207159478,0.013873454503077113,0.011004926227529549,0.008895683454675363,0.007485619177898257,0.006680022156266285,0.006387424430193112],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.905908659808474,4.883643161404619,4.8817389891275385,4.897101983347304,4.926080698629625,4.964983663622537,5.010500342949675,5.060015090275039,5.111809104127176,5.165149156251933,5.220264192760564,5.278212672128369,5.340645688643097,5.409474511093833,5.486456957594952,5.572725440745373,5.668305399876559,5.7718853385236,5.881050737228021,5.992660909113121,6.103220658104033,6.209216974127871,6.307403930892759,6.395027181827009,6.469984984075921,6.530925828558005,6.577284111170234,6.609255552088237,6.627713995373938,6.634071544604074,6.630085453354766,6.617618507777067,6.59836543433898,6.573566510789392,6.543741045470279,6.508518397475282,6.466784135930759,6.417092020056604,6.35810101126255,6.2889653171373,6.209645467959559,6.12111938534537,6.0254810188553,5.925920932299997,5.826589143454272,5.732346580283711,5.648418488932788,5.579971472396698,5.531651619914407,5.507115466729512,3.442968390844645,3.575525456808435,3.689188863350435,3.7836872140412074,3.859898985688348,3.919862675682658,3.9663067737429736,4.002064471623041,4.029594985543918,4.0506358588043945,4.065996658066315,4.0754987491742884,4.0780609904946346,4.071926476035696,4.055019913829902,4.025417950477458,3.9819051798817346,3.9245255488821797,3.854728334922411,3.775045490646841,3.6886833805398527,3.599129406635324,3.509799451582297,3.4237416470447597,3.343404355451953,3.2704713050949312,3.2057641982972576,3.149212220722484,3.0998880203102543,3.056110171285135,3.0156121602578816,2.9757767993941773,2.9339319883429793,2.887698323073371,2.8353708808680693,2.776304656452756,2.711157675138022,2.6416782506286536,2.5702433614054576,2.499403308588491,2.431480639973862,2.36824565351417,2.3106821478871553,2.2588510232153025,2.2118554301783346,2.167908596765405,2.124503240251161,2.078678595305866,2.027376678928827,1.9678729118472071],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[3.7965335580594815],"y":[5.013611148163598],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0005283532403099045,0.00048299732584098065,0.00047125507956924476,0.00048730946707455845,0.0005277517246496629,0.0005905449762644241,0.000674274524185547,0.0007778637374438102,0.0009008234783435334,0.0010439913820867843,0.0012106179349094532,0.0014076033647843517,0.0016466799977679716,0.001945303257500277,0.0023268469818069834,0.002819295208452804,0.003451145900209033,0.004244812394913112,0.005210147085247399,0.006338775323406302,0.0076006716962570935,0.00894461408564047,0.010303099043397207,0.011601059469603882,0.012766823914898515,0.013743377397508331,0.014497999082504057,0.015028539808348765,0.015364834336469076,0.015564053828300721,0.015699335578787083,0.015841908328514447,0.016038376051869203,0.016290452352754708,0.016548676485245637,0.016718804285812197,0.01668206989363889,0.01632630335384538,0.01557737673103757,0.014422142354260889,0.012916879089619247,0.011178958832088205,0.009363384564685606,0.00762987117652969,0.006109811919036718,0.004883932636214662,0.003978119547455646,0.003376780177627304,0.0030450755938535245,0.002948992543031849],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.5684466272314745,4.555117899206872,4.558076057018069,4.575026254384327,4.603236177709414,4.639906790496799,4.682473126829002,4.728827867715111,4.777464444987706,4.827539237558198,4.8788544004703684,4.931764564397158,4.987012712529612,5.045503618672188,5.108027824436347,5.174955458111631,5.245936821124397,5.319784003208837,5.394666234315999,5.468399404338625,5.538727979538544,5.603576119127385,5.661253388454609,5.71060601614968,5.751108506363404,5.782892881891758,5.806714422726894,5.823854109574371,5.835959752319554,5.844830629655051,5.852154943233817,5.85921582035776,5.866592988950883,5.873970947870852,5.880199131129726,5.883476510875628,5.881624396551974,5.87242570814218,5.853954462358419,5.824860492940233,5.784589452701239,5.733525500837681,5.67304984087915,5.605512825679806,5.534121343446785,5.462747345417814,5.395668195273985,5.337254517526978,5.291611471784249,5.262162167396656,3.6752712817560966,3.794507787232929,3.9014258348418602,3.995766218514203,4.078111058231951,4.149907386245252,4.213102147990471,4.269682342182964,4.3212952880716315,4.36896727578085,4.4129286717067435,4.452549826255212,4.486389049159393,4.512350986133621,4.527950279325532,4.530670798636689,4.51840456358776,4.489916288910697,4.445096789634493,4.384969270340802,4.311591058515114,4.227769074318627,4.136704931827135,4.041661581683777,3.945674608787188,3.8513211151289317,3.7605532079839796,3.674599065409801,3.593932055835686,3.5183069029221006,3.446860770111778,3.3782757300021795,3.3109967560201357,3.2434956094994334,3.174565509885193,3.103622930141228,3.0309149097952846,2.957413568760927,2.884529084178107,2.8138137340869056,2.7466933213004134,2.6842446145848937,2.6270309455640777,2.575003291088608,2.527470831910983,2.4831425914095626,2.440239677340136,2.396675212674867,2.3502956682164733,2.2991726367335303],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[4.331948131471222],"y":[6.909021517750929],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[8.344396423199845e-05,7.280309651927916e-05,7.228901458842519e-05,7.987374442755324e-05,9.494004757271294e-05,0.00011727246892313517,0.00014634869665920477,0.00018103799392710988,0.00021983191725560912,0.00026158004831789566,0.0003065134670039248,0.00035729270368977983,0.00041997510279754197,0.0005050421424017779,0.000628705828327605,0.0008142773295054784,0.001092157298118806,0.001496656065615034,0.0020593268636154736,0.0027987120493541055,0.003709320121554739,0.004754563109760982,0.005867270123772528,0.006958423687205954,0.007931975359726976,0.008702280208751962,0.00921075503219505,0.009439009230228073,0.009416249168163538,0.009219072637932136,0.00896218788333195,0.008779433604994575,0.008795285852675198,0.00909206931027279,0.009681028536642619,0.010471220031857149,0.011258498861707994,0.01176594513654034,0.011734880565110531,0.011025456550979975,0.009674378278763891,0.007885072029883543,0.005957524160472964,0.004186942761272318,0.0027728874724081507,0.0017787299960555902,0.0011555266060384534,0.0008043628401386724,0.0006326781488221691,0.0005800606428175846],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.506974582505489,4.490607525140319,4.499777607631226,4.529729818855024,4.574939363619504,4.6298913637683246,4.689708389661365,4.7506110584096195,4.810206338087978,4.867603782957409,4.923362876572384,4.979276719945801,5.038000426605721,5.102538718146161,5.175618018798251,5.258984751196508,5.352715050518732,5.454932809759227,5.5622388873186805,5.6703566991414025,5.774759574966053,5.871225338226678,5.956286791513584,6.027561413070375,6.083952839192781,6.125721675753908,6.154425435922397,6.1727287149732355,6.184086877929664,6.1923112308869745,6.201032235613269,6.213090438779924,6.229908964051747,6.25109085108975,6.274537553471567,6.296748091467201,6.313254640982461,6.319198355211747,6.3099260149541845,6.281588927814267,6.231691229435598,6.1595192380292705,6.0664025788824505,5.955778053224276,5.833045208008271,5.705219284200483,5.58040407833769,5.467124044360185,5.373554670206818,5.306661994851159,3.7038207846869584,3.8955943949798555,4.071609731333412,4.23161035911567,4.376592833949399,4.508796699905358,4.630972260899175,4.745496378082245,4.853685888011787,4.955356957311088,5.048653351522534,5.130152798574965,5.195247166147337,5.2387777620513685,5.255890739605391,5.243014202844184,5.198511300140733,5.122856160401623,5.018528542509786,4.889696834948538,4.741879111035671,4.5814476791780905,4.415048502952732,4.249044766248199,4.0890319918602245,3.939453504642943,3.8033322120292805,3.6821263085525686,3.57571197989455,3.482494132366016,3.3996449338828207,3.3234677370382437,3.249878993190717,3.174991474419773,3.095767445505481,3.0106871519644693,2.920199037110465,2.8264600302086507,2.7326664385349777,2.6423696039003444,2.5588608401365134,2.484666530745739,2.421177512864878,2.3684256504288212,2.3250138644479956,2.2882021565791524,2.2541493682522273,2.2183065785652554,2.175951385324516,2.122841613505034],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.587056987370298],"y":[7.691138525684522],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0,8.698554203045079e-25,1.623619298661053e-08,3.655415036244262e-05,0.0007046955338102291,0.003005991896860502,0.0065407876240353895,0.00969221077948311,0.010882066813407244,0.009417186418237307,0.005894494368677824,0.0021651861047840954,0.00024565739729731466,5.890444744258549e-07,2.9901248973241963e-22,9.91328598577342e-226,2.1653566175059905e-12,1.3468101319539288e-05,0.0006941140142214571,0.003476593360402428,0.007529211436883851,0.010714506406092408,0.011603543008693479,0.010001852327719295,0.006755981906155952,0.0032972931229989203,0.0009509971211740053,9.80189147223561e-05,8.090059936560982e-07,1.1803642099358102e-12,8.303559344017288e-42,0.0,1.3708807580926702e-126,1.1169586570300156e-120,5.977425123651932e-101,5.6820728993879995e-50,1.5909709765010299e-15,0.00010921592658045284,0.10247444295293474,0.2752087219296989,0.4196868660646716,0.5129513839109431,0.5286142743028674,0.44038459479225517,0.23103365048522684,0.005299205137663439,2.6316369953722032e-76,8.880101699643955e-70,1.3908658457249528e-145,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[2.8551290177121422,3.136857747883641,3.8301290586562646,4.781943004254803,5.81592010343646,6.76621609564118,7.498488325149411,7.921011607436423,7.989542501614188,7.708730821369984,7.131440646509445,6.355686898921646,5.517299762600579,4.775224553476526,4.2860964155886,4.166252450727258,4.445573373622288,5.049536268453369,5.836977314670087,6.64644503479056,7.330527417817886,7.777474696172249,7.922653982933598,7.7528637996871375,7.305613462643527,6.663959239336917,5.946007544549145,5.287343420590473,4.815200954566043,4.61620746925414,4.705979346203553,5.018141541766383,5.436621704133843,5.878508410941112,6.32512021778686,6.7556717259710135,7.158856723183993,7.5329347052310345,7.894711835274651,8.284481427145373,8.681312258582166,8.981867957727015,9.056315462922418,8.818853312824963,8.26335574674558,7.445634916713615,6.428497202522309,5.242181162891001,3.92707004557826,2.623781362340391,2.6141327161210017,3.882771940864619,5.201473652208859,6.418701573855823,7.343961386462325,7.907734705367256,8.179380141121229,8.281364411206729,8.302879414319307,8.261394415477818,8.124122677178057,7.867644283090045,7.523475659570601,7.147698960713569,6.747161205676787,6.316600837678588,5.866063456360887,5.418293487557877,5.008527354313857,4.5991261486107815,4.097091302660224,3.4402473041133947,2.6371508588065105,1.7612820417918935,0.9238988055616368,0.24372526945824635,-0.17782165966104158,-0.2737305351841073,-0.021780802941202992,0.5502092102818308,1.3635174262196945,2.2927530700880423,3.1774303951983365,3.8440721191473384,4.141594466906811,3.989566698136069,3.417877134666237,2.5476172456508737,1.5425726661816226,0.5697295209075421,-0.22697290945702964,-0.7417147648633451,-0.9142200977466053,-0.7327461335970935,-0.23461757747445944,0.49532080686787827,1.3296164384870353,2.1091926919613964,2.663883633573373,2.8454534238731015],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.103586633859458],"y":[8.331261799710944],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0,4.6006620049523106e-35,2.2850887388941583e-11,1.2349357972364261e-06,7.240599441974159e-05,0.0005089483652568077,0.00141105615023162,0.0023145890231480444,0.002598063435801204,0.002029017300308247,0.0009931170279281988,0.00021804511519206966,7.565918502783963e-06,4.704157918442892e-10,4.270645369248049e-36,0.0,1.266623058808536e-19,3.699346188138687e-08,2.1230048413631965e-05,0.0002586339413349799,0.0008236527424160322,0.0013609151610708729,0.0014713980180198788,0.0011081524009816162,0.0005574016060328355,0.00015860568235703937,1.693974149928131e-05,2.355318240658295e-07,1.5847571264854433e-11,3.4622866769315605e-24,1.0247307393775345e-94,0.0,0.0,0.0,0.0,5.486808318163093e-256,6.724060148422914e-117,1.843628158197414e-64,7.410564789538639e-15,0.000570854046040476,0.01053658310134061,0.015383865117828523,0.009552364606789949,0.0049345930285780186,4.302953822845676e-05,2.949985119638589e-22,0.0,1.6305352544978261e-220,0.0,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[2.8524657468214603,3.12952033035516,3.757487176596706,4.604870467574438,5.521091893815866,6.362093385282682,7.008816238643921,7.379225189895277,7.435011302520133,7.183958553324761,6.678446497786515,6.009915732776687,5.298559944697798,4.677264541062574,4.269173288255161,4.1595494749750275,4.366127748088958,4.829385316832487,5.437902532093004,6.061404143109643,6.5784655486374035,6.8967229701921795,6.965403719498402,6.780734438760591,6.384809611482695,5.858216753838953,5.30652014102836,4.8410041608975956,4.555272514776986,4.501699075009389,4.675221572468226,5.01521586679053,5.435155390544143,5.875888914233714,6.320681202997724,6.754938461808704,7.167489400625382,7.539128079462647,7.851489979449614,8.098202219023278,8.261471551657463,8.333937030974086,8.324996622747447,8.206027234545104,7.890263802808923,7.301502210301452,6.424947905444637,5.295779187195145,3.984102650760243,2.6185082814889697,2.613751054394086,3.9617065736934363,5.277057705326164,6.420187361837482,7.275183654394494,7.838340161485196,8.16927013210076,8.317671998537657,8.319779427866935,8.22371675443919,8.06621280332897,7.841824015390671,7.53450316274306,7.162188259400966,6.750612785223062,6.316337894038885,5.869366826978794,5.424786352592191,5.010460948499867,4.609496671867591,4.160761330946,3.6129137213276064,2.9593948127526937,2.2442286470426875,1.5485167610122077,0.9686942008990309,0.5942900634365995,0.48938199574733465,0.6794927747831143,1.1444537630572724,1.817444166819254,2.5906033583859593,3.327903196089125,3.885956954264269,4.142725231001319,4.03212172152882,3.5708285747766717,2.8476426586692103,1.991920245115633,1.1440847346678336,0.4323256181530808,-0.04398810093927841,-0.22490617844648764,-0.09556862394520227,0.3122501855266169,0.9225003566715886,1.6215462718829794,2.270129776833955,2.721695658901528,2.84769580253708],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[4.993654014104051],"y":[8.348254087751911],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false],"title":"16"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false],"title":"19"}],"label":"i = 6","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true],"title":"22"}],"label":"i = 7","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Upper Confidence Bound (UCB)

Choose the next point by trading off between surrogate's posterior mean and uncertainty.

$$
\begin{align*}
x_{t+1} = \arg\max_x \mu_t(x) + \sqrt{\beta} \sigma_t(x)
\end{align*}
$$

In [80]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=UpperConfidenceBound
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)
results["UCB"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:21] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:21] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 09:43:22] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [81]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="f4f261f4-bb09-44ab-84be-88a74e2ab571" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("f4f261f4-bb09-44ab-84be-88a74e2ab571")) {                    Plotly.newPlot(                        "f4f261f4-bb09-44ab-84be-88a74e2ab571",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.5385537455963063,-0.586919132471347,-0.6353555829071795,-0.6834275172359378,-0.7306248079001517,-0.7763541519346802,-0.8199287658387051,-0.8605552153030349,-0.897315243803269,-0.9291389589480386,-0.9547638702576812,-0.9726741465483395,-0.9810253962753392,-0.9776108885815831,-0.9600583667768401,-0.9265613037683571,-0.8770132383870983,-0.8133804260585877,-0.7387206493432023,-0.6560692544643613,-0.5679836547461643,-0.4765359212254989,-0.3834248644437226,-0.2900741243979332,-0.19769333173470782,-0.10730902652184487,-0.019774021337617576,0.06423938655426303,0.14425954945891076,0.22004624022986016,0.2916244349646481,0.3592985766156801,0.42359611088465926,0.4850656492096811,0.5439126580066164,0.5996628156545168,0.6512023207783356,0.6971815842352724,0.7364206221845143,0.7681279177031611,0.791968029180581,0.8080734775267988,0.8170640008159974,0.8200909417511887,0.8188691337476174,0.8155700173953773,0.8123905876617088,0.8108293232923862,0.8112170583316103,0.8129835691100369],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[5.28214746108094],"y":[8.062511138469858],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.3645544599693048,-0.40620889697438295,-0.4487693572292339,-0.49192446251275784,-0.5352867931952072,-0.5783809667447924,-0.6206302365267578,-0.6613417172991769,-0.6996908783446095,-0.734707209821059,-0.7652656554245167,-0.790093446698328,-0.8078097463659468,-0.8170232570448337,-0.8165106445340357,-0.805470278608273,-0.7837843463918496,-0.7521019716974495,-0.7116312674951332,-0.6638439501296887,-0.610234563847381,-0.5521738522199584,-0.4908427898560223,-0.42721627164676834,-0.3620706508665546,-0.29599995394036943,-0.22943391205926533,-0.16265600006365405,-0.09582268167457597,-0.028987258501393776,0.03786622588228028,0.10477179492431296,0.17170559767877988,0.2384816417742628,0.30462628455505275,0.3692708242365497,0.43118429861835716,0.48894474321941783,0.5411367947973023,0.5865383405029793,0.6242835810080976,0.6539958781882218,0.6758757202486636,0.6907123257587958,0.6997878473159334,0.7046478498566683,0.7067206022031154,0.7069921589392384,0.7059138541771491,0.7035878155004716],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[8.089770783263793,7.860703606414598,7.622117300893126,7.376099688338648,7.1253219785175155,6.873069748980079,6.623248354985064,6.380352899230695,6.149391768108006,5.935752228225059,5.744997078470032,5.58258337413377,5.453498361348393,5.361814567530566,5.310175925435652,5.299239875807018,5.327143502321956,5.38943477851384,5.479778491746931,5.59080935235496,5.714888049790666,5.84473582507414,5.973937716933844,6.0973122090921255,6.211149692918072,6.313324411622921,6.4032851704564395,6.4819300423332695,6.5513705965315605,6.614592876266389,6.675026473408285,6.73604051585881,6.800396840039718,6.86970610537781,6.943951357454329,7.02123206846183,7.098170925213172,7.170833401164502,7.235622256157267,7.289998308777529,7.332970781549623,7.365330749429897,7.38962938420428,7.409928660757309,7.431374597500959,7.459632097178986,7.500162634007157,7.557375773358315,7.633914594137186,7.730588830641307,6.057821125822733,6.230772420779854,6.371089301576157,6.476336139352336,6.545461224194559,6.5788961681584315,6.57849542239355,6.547538323694363,6.490510558127817,6.412296036017706,6.317348203152218,6.209111962187286,6.089735703082352,5.960086505855439,5.820057379900498,5.669128591613826,5.507115907422042,5.334960267867072,5.155100335004108,4.971280644884314,4.788145989892904,4.610759434375058,4.444109019682951,4.2926493069475855,4.159908160836719,4.048177439531344,3.9582984796420484,3.8895487960916713,3.839634325606318,3.804790792464836,3.779997306493481,3.7593040739037846,3.7362731330785035,3.704525497667028,3.6583795253964198,3.593550986385698,3.507730674810319,3.4005898048328476,3.2734146272854217,3.128687205120473,2.96967844483979,2.800084369444627,2.62372251482942,2.444294529204493,2.265213518386304,2.0894899480624605,1.9196673836692617,1.7577984227955428,1.6054513354061761,1.4637387576621972],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[5.715464231391885],"y":[5.7787487222264815],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.4134886197966897,-0.45455734654670155,-0.4968745571657266,-0.5401341389664015,-0.5839413156600692,-0.6277971917928746,-0.6710813125660736,-0.7130323705440398,-0.7527278176722061,-0.7890646165350805,-0.8207465138281738,-0.8462891956131811,-0.864064098433035,-0.8724115757131474,-0.8698529598639331,-0.8553993566887226,-0.8288810588370025,-0.7910574138038355,-0.7433578973910886,-0.6875235595871645,-0.6253226531389444,-0.5583809485831153,-0.48810694968801366,-0.41567444135838544,-0.3420322054535073,-0.2679233950974983,-0.19390662722791885,-0.12037664009079979,-0.04758592027585479,0.02432848576723784,0.09530589138793927,0.16530080996971824,0.2341891420803035,0.3016361380649871,0.36693535502046004,0.42887065774623934,0.48575744727800374,0.5356591951261093,0.5766346679482592,0.6069706907311291,0.6253949414097821,0.6312802383864801,0.6248503638174534,0.6073709745403796,0.5812554232376044,0.5498735910367925,0.5167823601568517,0.48477712556070046,0.45534888090941783,0.4288731299785815],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[7.576300754476621,7.399635932766348,7.212976444204291,7.017743821689516,6.815917149801075,6.610092318577717,6.403521627786201,6.200122507013764,6.004441928939392,5.821561341955104,5.65692614511161,5.516084567874959,5.404324170014147,5.326201019632968,5.28496783320163,5.281923380666701,5.315757910066951,5.382409802064481,5.475806973348677,5.588773054151802,5.71381771963976,5.8437874049713905,5.972370993502309,6.094464072793638,6.206399984830421,6.306056958048309,6.392849286957459,6.467608136148658,6.532355443601211,6.589973965377437,6.64377915101628,6.697005657735562,6.752234098102101,6.810802656912812,6.872273114200918,6.934126560972997,6.9921956865557755,7.041671805235057,7.0780864956820935,7.098109589986862,7.100111119604184,7.08446953324168,7.053639856567529,7.01202396419479,6.965707464856334,6.922033247018113,6.88875903062333,6.872863262483258,6.879288417619,6.9104013765599435,5.822273132560526,5.9912315208525335,6.131473200357386,6.240537467006419,6.317258108938576,6.361776532783678,6.375464578991521,6.3610345630503895,6.32246307670857,6.264189492797135,6.190245233462045,6.1036398985259215,6.006050309329502,5.897830956053315,5.7783394126480125,5.646541724892816,5.50183021782603,5.344893706028416,5.1781085967511755,5.00528892320304,4.831217004282355,4.661114692425046,4.50012438754282,4.352844083976038,4.222941523406904,4.112859521836505,4.023617129870907,3.9547082672096545,3.904099440399525,3.8683296805528062,3.842717522904155,3.821680313818009,3.79916902737602,3.7692158792300603,3.726581493635981,3.6674700149148265,3.5901078610879296,3.494695390876932,3.3829653801445367,3.2577041046273383,3.122308549513858,2.980410819165079,2.835583172753023,2.6911245397058647,2.549921416427718,2.41437178001636,2.2863590659595414,2.1672634466752116,2.0579988983109385,1.959066323815064],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[5.0165540567741385],"y":[8.353042361423036],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.36274088699771156,-0.3881799851477882,-0.4184122481783814,-0.45422181423564867,-0.49645855090730473,-0.5460132397436911,-0.6037764910343892,-0.6705765353418018,-0.7470905966398264,-0.8337244806212194,-0.9304554217959884,-1.0366335043447155,-1.1507316383837898,-1.2699792663108902,-1.3891004041680317,-1.454132961531623,-1.353286213510054,-1.2415720782684567,-1.1338134954298575,-1.033908370931564,-0.9440423343477122,-0.8653142950192151,-0.7979970859129981,-0.7417107382123834,-0.6955344459615816,-0.6580597598771463,-0.6273865917172258,-0.601065928089213,-0.5759966676744728,-0.5482889678365598,-0.5131119229335825,-0.46453606231792366,-0.395233462386914,-0.29320312928481157,-0.08414411934622121,0.19984122837017676,0.47523647866274965,0.7245636440531938,0.935018864971134,1.0958779325158234,1.199065308195765,1.2424110037996832,1.2148695291645935,1.0737436330425894,0.8121193129701074,0.43121331247149314,-0.045370321918906026,-0.5257505253715541,-0.9316041302614675,-1.2511332278229312],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[12.56345373133549,12.35626091083674,12.093520159625392,11.764123007086429,11.356736043566272,10.86096607367824,10.269131261165466,9.578728728478108,8.795586756999981,7.937489832493709,7.037734057286789,6.147593199980982,5.336087492708497,4.684890050715658,4.275996588296173,4.170453723850872,4.380007698977817,4.855326550110301,5.509292197208063,6.243762579055863,6.967345472614708,7.604862399730535,8.100828866082617,8.419479978921196,8.543425584797543,8.472342389867212,8.222408316783635,7.826514337123495,7.33463696214579,6.813106297987871,6.340920150204285,6.000955423372265,5.864391133742632,5.968660468586983,6.293701019272335,6.752450228523464,7.227830689813137,7.630573040959817,7.928507849296807,8.138147399184959,8.28677634751282,8.367861745803182,8.326563745509945,8.106692260901758,7.695648880240936,7.102626938994457,6.371377777239635,5.613624812565279,4.983736200654257,4.600415600136827,3.940189100944672,4.775688640562266,5.579887195518154,6.357633468155488,7.072585924044096,7.6677365529465416,8.087014175299975,8.3076607340964,8.346495331798138,8.209825254091875,7.912985551767977,7.516836663468899,7.109909392365481,6.762382259103688,6.487531361672997,6.232682892297781,5.907184283416737,5.438145789736037,4.808357097308292,4.050988145136694,3.2291859776210066,2.416199017527731,1.6811690496537266,1.081174039026556,0.6580222555193802,0.43777758154640534,0.4312532808141243,0.6342649682915309,1.0270579771825696,1.5729566517207059,2.2169348419995436,2.8854897586387382,3.489854990942269,3.9350036077496533,4.136649144780818,4.046764110383214,3.6756499421015296,3.0807503165414047,2.3395987403161214,1.529372396419225,0.7150116839175418,-0.05566324187737681,-0.7521209875874355,-1.358676035663219,-1.8710020733806534,-2.2925956490458814,-2.6317169583276376,-2.899010475823361,-3.105812581667477,-3.2630537702004165],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[5.045794885225497],"y":[8.352948194884533],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.6360814102529371,-0.6525555475115393,-0.6729752157076666,-0.6981418854263717,-0.7289552720837588,-0.766399125890082,-0.8115134558287226,-0.8653486162066143,-0.9288959318384364,-1.0029889360190651,-1.0881690576420027,-1.1845100419743242,-1.2913968808936265,-1.4072571498729758,-1.5292318880899427,-1.6077938448838565,-1.49058046523736,-1.3790684696619881,-1.2770090789025101,-1.1864436950365274,-1.1082833346326577,-1.0425627335838519,-0.9886363752461993,-0.9453172794618773,-0.9109586605428512,-0.8834814220250699,-0.8603530740722093,-0.8385265807439963,-0.8143519432742058,-0.7834804048151537,-0.7407929409582855,-0.6804037473411751,-0.5958168409613929,-0.4802747530096896,-0.24964146805436765,0.052410802234749754,0.33372487914019877,0.5794751109485696,0.7775980699032167,0.9194499434201546,1.0002499013587423,1.019717289036653,0.9889724474923199,0.8618736154502842,0.6519947297174815,0.307953477842337,-0.19541907217864654,-0.797587158782355,-1.3834070141344537,-1.8878524812419435],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[14.899487098845947,14.59731824625456,14.219299303029757,13.752573302449534,13.184908973420045,12.50629333222417,11.711155560461776,10.801245388207903,9.789054259773252,8.701440274025298,7.582779828056482,6.496525298267478,5.523557081900988,4.755332914857103,4.279850256945082,4.159288377387758,4.401687111531412,4.949738428555891,5.704339242251746,6.552252234819074,7.385596009375586,8.113398437382568,8.667095180999294,9.002207970879372,9.098139325732944,8.957422472041884,8.605068993439598,8.08795015561714,7.4734659139563195,6.846145746387824,6.300416096830881,5.927840723195359,5.798178219339359,5.93625889353408,6.30148458813715,6.787046172700685,7.267471551058512,7.659951544891383,7.946252560064422,8.150426982512341,8.29220366903258,8.353690466491,8.296126679967244,8.101448379150634,7.75771517139026,7.210870616330006,6.423709561752764,5.46159286000988,4.4992454043535,3.7173729849391735,3.4363744798695195,4.448386089366773,5.459534061882181,6.4231928485077265,7.2065143041822495,7.753768893192425,8.100878037864577,8.293719029346061,8.353364606224746,8.269792707957093,8.03352553758157,7.673142112342545,7.262181253093345,6.879546555345489,6.558681308408256,6.261994347928036,5.89942624182173,5.386156493646027,4.690416252141956,3.837041100903333,2.8905934909793167,1.9346816090369696,1.0546214210789047,0.325696758424332,-0.193456140144602,-0.46390309769677973,-0.46757853228987933,-0.20785561994798218,0.28977780687320775,0.9769024424246795,1.7818699546774024,2.611372446976623,3.355817515431063,3.9007390033472946,4.146114545225724,4.033807505948925,3.570915495805598,2.81858575469758,1.863813383412925,0.7971554325291041,-0.30127334576935905,-1.3686421198749938,-2.3610573960803016,-3.2520187545426635,-4.0292842902159745,-4.69126371249193,-5.243614544617011,-5.696379529279881,-6.0617765403625725,-6.352617664133875],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.9993789174230505],"y":[8.349843198387447],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.796464324431568,-0.8121960086675974,-0.8318440902939169,-0.8561997518668545,-0.8861462728038825,-0.9226443155428149,-0.9667045364759566,-1.0193434292555343,-1.081517637643299,-1.154031414063758,-1.2374116104070108,-1.331744801912472,-1.4364720753084201,-1.5501380295854703,-1.6700777482577924,-1.7476382208868741,-1.6328984019018842,-1.5245444345197972,-1.4259975718809406,-1.3390442774742342,-1.2644037136188453,-1.2019612849805137,-1.1509443161970534,-1.1100438363122145,-1.0774842182643856,-1.0510445513735878,-1.0280379753978766,-1.0052580983039348,-0.9789059504970099,-0.9445179227124105,-0.8969264908469698,-0.8303034812669818,-0.7383606065495942,-0.6147336095956321,-0.3810172689731264,-0.0808528632588304,0.19842830063232972,0.44275086612839026,0.6409165875123386,0.7851381746784056,0.8711503538410656,0.898399340492169,0.8673460751281438,0.7404519246779215,0.5276293663742984,0.18085468117389628,-0.32472969151527276,-0.9314305584665407,-1.527875864420319,-2.0494747045627135],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[15.131163680845056,14.793425971981248,14.376228559970052,13.867659639665115,13.25695982290163,12.536144483045446,11.702174733262288,10.759658820866607,9.723933856755961,8.62416960777616,7.505842242835078,6.43155966647697,5.4788401499898,4.73318763685476,4.274911568255967,4.158949202708486,4.389962841629986,4.912797605312843,5.6334829821189345,6.44411969641588,7.2409310446980815,7.935510370006517,8.460715911296433,8.77302086885251,8.852923219512984,8.704533141916055,8.354858349973975,7.852688601300532,7.2663925750092595,6.679451080333329,6.182298089301333,5.859284910115759,5.770730128871854,5.932556859478343,6.300215400515167,6.771989855237504,7.23476122306415,7.618238152631982,7.910024196300097,8.129948381049752,8.286473817404215,8.353497617725283,8.296166782154828,8.101615778557067,7.756560007201858,7.20918082543622,6.4233917716398725,5.461225268407107,4.489480636557436,3.6809727051443843,3.4229645130906388,4.442762796454438,5.459252603272109,6.422885242441785,7.205320189774224,7.753156049852195,8.101082792601348,8.294393836153073,8.353328471826304,8.275020540858932,8.054811417725952,7.712554109384889,7.309440788545064,6.919055952180956,6.57981430303293,6.266106114804881,5.9000988282887565,5.402474429925359,4.738372081616255,3.924727437626209,3.0176111380568953,2.094204230553497,1.2364111556806119,0.5188374579889987,0.0012595765124698843,-0.275478503905064,-0.29148427898111073,-0.048866168092808415,0.4275430549277548,1.0897202038644433,1.8667839055917224,2.667256810226082,3.384871390796116,3.9097329495178834,4.146294635499876,4.038178248384177,3.5891183747524043,2.853363950977284,1.9107244119071365,0.8463501805152678,-0.26248123937455947,-1.353316955618995,-2.380771498571095,-3.315718380548933,-4.142829545361105,-4.8574817873661384,-5.462682841663506,-5.966375905939984,-6.379273074715096,-6.713236228633146],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.038983862056284],"y":[8.353604872575431],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.9202538824104529,-0.9361281076901904,-0.9559634328765323,-0.9805597387881465,-1.010809715070308,-1.0476839337978432,-1.092203141538557,-1.145393652830414,-1.208221053755085,-1.2814968588364621,-1.3657524694714844,-1.4610749891882888,-1.5669003712907343,-1.6817603835111794,-1.8029672159873853,-1.8813452868152323,-1.7653206911216284,-1.6557916751126793,-1.5561933687014187,-1.4683172131062157,-1.3928775108758797,-1.3297463276751715,-1.278130026265389,-1.2366914502324664,-1.2036195881149088,-1.1766506881862933,-1.1530471690628563,-1.129543608504193,-1.102273492532014,-1.0666975071812943,-1.017565672478554,-0.948963818813985,-0.8545202948424676,-0.7278015013410749,-0.49004459421484614,-0.18548331741287727,0.09799910025020273,0.3462436492169475,0.5480190764337439,0.6955399691521506,0.7845139501525253,0.8132552198705765,0.7813180391613506,0.6526007906376129,0.4356672010744566,0.08260531918789378,-0.43211500836373296,-1.0502361148624217,-1.6585833566111916,-2.191261666771573],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[15.010767877655201,14.675115076385527,14.26077834775662,13.756045613569139,13.150371176904452,12.435979307628633,11.610005334987935,10.677154208962277,9.652726469043914,8.565656947610911,7.460923553017993,6.400325535506802,5.460260747183061,4.724882263033541,4.273122131022453,4.158868138751297,4.386534341062323,4.901720795965945,5.611839318521209,6.41056524233714,7.195601120113388,7.879774482007088,8.396882583662189,8.704048843428335,8.782158749002221,8.635467133252204,8.29088288555173,7.796829869582867,7.2210069212029335,6.645893775601972,6.160610996087088,5.847996638583442,5.766909544525106,5.932282199727337,6.299570121339346,6.768434030660749,7.2280525628632875,7.610213384891543,7.903331062386096,8.126312714444,8.285562899872508,8.353562555737353,8.296229247464236,8.101623100930786,7.75641050428671,7.209134351406138,6.423462285229208,5.460969322899211,4.487851176940622,3.675858028389271,3.4229308351597676,4.442169939339741,5.459057064726086,6.422973820877711,7.205401068959955,7.75314361753708,8.101115454012925,8.29475131622086,8.353435689998593,8.275181805060276,8.056803456565278,7.717114370233848,7.315334159003698,6.924044891637993,6.582307825555239,6.266402555053479,5.900628718889338,5.406950271345,4.750495231964813,3.9472388051799028,3.0518428498734016,2.1400312191145203,1.292447063293769,0.5827382684478182,0.07004402123401832,-0.20513638722885652,-0.22299918082243764,0.014491578873689903,0.4828808456903464,1.1347774053167536,1.9002133820688476,2.688914342108518,3.3960571340947894,3.913286379899034,4.146406740047306,4.0397759646283165,3.596880181245991,2.870933950499743,1.9403920150868181,0.8890790107696467,-0.20682366238564764,-1.28564996066528,-2.3024941994604404,-3.228449913894181,-4.048214149110743,-4.757058647279818,-5.357811282566192,-5.858202971961673,-6.268730563917068,-6.6010560913442085],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[5.035939505891532],"y":[8.353772660864934],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false],"title":"16"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false],"title":"19"}],"label":"i = 6","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true],"title":"22"}],"label":"i = 7","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Thompson Sampling
Choose the next point by sampling from the surrogate's posterior (or a sum over a batch of samples) and then optimizing along this trajectory.

In [82]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=PathwiseThompsonSampling
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client, acqf_n=5)
results["Thompson"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:22] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:22] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 09:43:24] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [83]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(color="red"),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="8d62cdb7-5527-4ba4-b11d-7bd28ce4a8dd" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("8d62cdb7-5527-4ba4-b11d-7bd28ce4a8dd")) {                    Plotly.newPlot(                        "8d62cdb7-5527-4ba4-b11d-7bd28ce4a8dd",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.3373965250666634,-0.46323591451457014,-0.5861176043555345,-0.705407788218475,-0.8196226151268932,-0.9266074327990229,-1.0237757736652342,-1.1083812359921998,-1.1777935728191529,-1.229751415238323,-1.2625679101985714,-1.275271657548396,-1.2676729791612766,-1.2403538977611217,-1.194588349891181,-1.132206259403321,-1.0554201633760814,-0.9666324116371655,-0.8682420073805449,-0.7624769521624861,-0.6512702759999981,-0.5361901909043185,-0.41842809347461807,-0.29884130753738836,-0.1780412454716691,-0.056512778718504686,0.06525241460159625,0.18662658947252053,0.3067373916817777,0.4243931391701966,0.5380498205440445,0.6458213865338481,0.7455281792476165,0.8347719229267639,0.9110203563253795,0.97169841538787,1.0143631474676593,1.0369371468836797,1.0378939859921363,1.0163748964883257,0.9722352566985487,0.9060253735881586,0.8189159174289127,0.7125835440725713,0.5890761495108258,0.4506794312992878,0.29980677622259433,0.13893115090104624,-0.02947369961479096,-0.2030588233004218],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.0670857509094227,-1.117117228153696,-1.1276737351273871,-1.1071476141287244,-1.0682211794497996,-1.0249207555489426,-0.9895220339952779,-0.9700886946227378,-0.969235756264635,-0.9843646192849835,-1.0092139052640356,-1.0362197720451731,-1.05897692975804,-1.0740913234198668,-1.081915577078037,-1.0860016917399282,-1.0914868185330768,-1.102837859552469,-1.1215681940935776,-1.1447811038065783,-1.1650546106400397,-1.1717579058815049,-1.15349216747104,-1.1010276356688615,-1.009953074950825,-0.8823085554392583,-0.7267258133460277,-0.5569858787850559,-0.3893182632573873,-0.239098246531826,-0.11775888351916297,-0.030678649345125958,0.023451333166661724,0.051666012234994285,0.06447409760658598,0.07293947412251928,0.0858260278677615,0.10755323265767813,0.1375164799494799,0.17089103854428056,0.20062607806746624,0.22001842595731547,0.22511081124725496,0.2162245075913929,0.19819198888320888,0.17922969184356874,0.16878010307246405,0.17494742806266506,0.2022483383516105,0.25029253795822126],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.1319087805396488,-1.137088190062732,-1.1452229682240982,-1.1593089484892487,-1.1815513098727968,-1.212958297119164,-1.2530535174458652,-1.2997458475479737,-1.349379138665137,-1.3969642652331828,-1.4365757967826653,-1.4618769472900255,-1.4667215754225547,-1.4457725830853965,-1.3950732119447296,-1.312511876716345,-1.1981307208662977,-1.0542280235490786,-0.8852267405359571,-0.6973411026600552,-0.4980785959619435,-0.29562399311222876,-0.09816512021544821,0.08677316569430471,0.2529206978633356,0.3957208792996785,0.5126121064228408,0.6031059389810218,0.6686578998185035,0.7123489904911798,0.7384163227077498,0.7516874799805714,0.7569835687865165,0.7585592613269776,0.7596440772543711,0.7621331250852993,0.7664353241997349,0.7714958342027907,0.7750110549655912,0.7738097780017889,0.7643518784332008,0.7432830352167412,0.707977849163208,0.6570051428237034,0.5904581146098912,0.5101075022987269,0.4193563789999202,0.32299785483369303,0.22678381954964288,0.13682066437674267],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.40143077202517935,-0.5201923622337324,-0.6184043335703493,-0.7003866852167149,-0.772180133427006,-0.8402108924635652,-0.9099442906884722,-0.984764170964576,-1.0652713420456923,-1.1491170838616596,-1.2313909829262744,-1.3054836599074422,-1.3642619203586182,-1.4013412014912903,-1.4122269946892625,-1.3951251013653165,-1.3512829462117053,-1.284790275790308,-1.2018658319754323,-1.109792815713485,-1.0157059737525487,-0.925446620985203,-0.8426870412510172,-0.7684744790390083,-0.7012669173326818,-0.6374426132161919,-0.5721795562515435,-0.5005352278371233,-0.4185230052231974,-0.323985018991078,-0.21710100303194535,-0.10044075093557536,0.021448868620622896,0.14284855819832298,0.25792219600381716,0.3618192423067388,0.45150043068518975,0.5261409389139076,0.5871452592960251,0.6377714684632523,0.6824242894833348,0.7257448136675886,0.7716673315644657,0.8226224083940403,0.8790385983507968,0.9392381873675851,0.9997459701181086,1.055949689603293,1.103001968898547,1.1368248654674653],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.1325969542051573,-1.0956286041305807,-1.0570217765608807,-1.0171291762065462,-0.9779603746038013,-0.9427992657705998,-0.915393644573288,-0.8989165408904957,-0.8949599257689569,-0.9028206755105157,-0.9192759493254072,-0.9389344902220815,-0.955117054756763,-0.9610938806925136,-0.9514188686065843,-0.9230697630421106,-0.8761384304928022,-0.8139041918654288,-0.7422551169920949,-0.6685729655052554,-0.6003102562419927,-0.5435536517654395,-0.5018715633645696,-0.4756822979987658,-0.4622659009711726,-0.45640344340191524,-0.4514930499279392,-0.44089243550333623,-0.4191951137069627,-0.38317081207766335,-0.33218410180908364,-0.2680293877618076,-0.19425669237519894,-0.11518002029462249,-0.034831874992543366,0.04387571281612579,0.11963920937301098,0.19278139653945692,0.2647458083106895,0.33720325011657226,0.4110093607955567,0.48529000609608697,0.5569052035627029,0.6204580983689469,0.6688924819622062,0.694588778672308,0.6907552243369177,0.6528411204988633,0.5796046136871231,0.47345460576132226],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[3.5404561478325185],"y":[4.20264814790707],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.510532107179071,-0.43359033624090615,-0.34975301957108923,-0.2663906760515237,-0.18958104137889398,-0.1227739706878356,-0.06626566843236745,-0.017588622486334304,0.02730676295053175,0.07240259983159675,0.11994050561130148,0.16918151391507474,0.21595426183695537,0.25315584263548424,0.2721334609744525,0.26464952883189635,0.2249751523615494,0.15163869171102873,0.04841590239443316,-0.07576654824717921,-0.2080648370180156,-0.33386347849377307,-0.4393951902280786,-0.5142805620066555,-0.5534384642960841,-0.5579468564185712,-0.5346577424953785,-0.49463941198643924,-0.45077288792560344,-0.4150098769703938,-0.3958703041057068,-0.39678852129001485,-0.4157628242238851,-0.44624216156843377,-0.4789925265935775,-0.50452690596159,-0.515544545509746,-0.5088291839248915,-0.48618475323762245,-0.45419829723956595,-0.42288588895896684,-0.4035314018282865,-0.4062106068188759,-0.43756273695553494,-0.49931298883274056,-0.5878765551133511,-0.6951279934522145,-0.8101554344214198,-0.9215818152044807,-1.0198951765991882],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.7785635162751956,-0.7361228812848574,-0.6945700406882184,-0.6551228705404618,-0.618865320846703,-0.5867039795655475,-0.5593319482245225,-0.5372015158306034,-0.5205069460051839,-0.5091785548084453,-0.5028891778615545,-0.5010741293410581,-0.5029658656969471,-0.5076448058219125,-0.5141081476737961,-0.5213590777957644,-0.5285143736616915,-0.5348605038133996,-0.5397975377110062,-0.5427697638110567,-0.5432167810202906,-0.5405429183329373,-0.5341031216354808,-0.523204447719709,-0.507123240091557,-0.48513893528293495,-0.4565862699144747,-0.4209284384701379,-0.3778545042569642,-0.32740511061340066,-0.27012451466897386,-0.20711413102290638,-0.13982957139899765,-0.06980560633102095,0.001611776463971537,0.07350559235916121,0.14542441862415667,0.2172367096735014,0.2889851809140488,0.3607666727199813,0.43263667186265,0.5045383688940497,0.5762568015698717,0.6473992096268804,0.7174032307215414,0.7855750311375231,0.8511599225439908,0.9134464599660836,0.9718514857008546,1.0258901711927062],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.39120330843595474,-0.5516011221797193,-0.7079896658329734,-0.8578596570194703,-0.9991587545664568,-1.130191944561155,-1.2494993114107507,-1.355734531095084,-1.44756617407095,-1.5236197587966849,-1.5824719316051246,-1.6226999172366126,-1.6429804275635012,-1.6422235552969577,-1.6197197998019996,-1.5752731094202528,-1.5092947851097969,-1.4228940232849325,-1.3179971297242843,-1.1973941904564827,-1.0646782423759809,-0.9240835922506873,-0.7802397014869836,-0.6378651076139026,-0.5014319313116631,-0.37483488551901223,-0.26109892771947,-0.16215669539971245,-0.07872091665238679,-0.010268704320338662,0.04485612308414838,0.08924536936779964,0.12617070044718942,0.15926317337569185,0.1921426436680671,0.22803953612022365,0.2695056905433374,0.3182380985687181,0.3749764103774524,0.4394806104611363,0.5105943739811253,0.5863894434102661,0.6643773536865754,0.74176795956841,0.8157502003752313,0.883769789173233,0.9437811013543711,0.9944544871245269,1.0352837377509723,1.0665117595296456],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.2688283055804743,0.16675553750760022,0.05812139863329009,-0.0535711061313241,-0.1638819519067927,-0.2678113556910083,-0.3602755221878631,-0.4366240776500901,-0.49313606130703913,-0.5274329371236363,-0.5387564955419795,-0.5280756553574413,-0.4980071343019449,-0.4525582158704653,-0.396722588703053,-0.3359797141639592,-0.27575907690678225,-0.2208977699729,-0.17512288125150755,-0.14067124145802512,-0.11810461480446355,-0.1063357943902461,-0.10285689023293698,-0.10413792170157765,-0.10614399951408471,-0.10490529787748804,-0.09706736537659255,-0.08035088611956942,-0.053859557407545555,-0.018191092791060903,0.02467029087098105,0.07163713705136843,0.11890124913150713,0.16243398196683323,0.19857460659201642,0.22462067420923137,0.23924270808401715,0.24267285324147192,0.23672969779105202,0.22467119749662245,0.21087675652203464,0.20038389898556863,0.1983258644952004,0.20933141868709804,0.2369554735182251,0.28320794656970283,0.3482388355502002,0.43022069599692947,0.5254425730918941,0.6286007668679532],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.8195303741321391,-0.815940996507279,-0.7904541215018779,-0.7483327246603803,-0.6963516936649724,-0.6419605837516346,-0.5924524425031331,-0.5542268301112812,-0.5322141450191551,-0.5295015033413781,-0.5471721472234636,-0.5843448124365939,-0.6383798763153729,-0.7052072773326592,-0.7797274669189765,-0.8562399397053161,-0.928862580390321,-0.9919223675630209,-1.0403072807107998,-1.0697612512521135,-1.0771150352129988,-1.0604506316231472,-1.019195611381412,-0.9541416466838069,-0.8673805957455946,-0.7621533144213456,-0.6426118567011302,-0.5135048416413415,-0.3798074206295203,-0.24632951842862177,-0.11734434802194262,0.0037517984323936493,0.1147479908056854,0.21480025978902223,0.30443769393722453,0.3853899603905008,0.4602458976337799,0.5319884961410138,0.6034800929027367,0.6769702084826097,0.7536962593234503,0.8336366214643183,0.9154554892070323,0.9966524101067359,1.0739002316301716,1.1435279843246065,1.2020843066347542,1.246904901691484,1.276583055600401,1.291234249665936],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[6.597104567533039,6.458592465956468,6.314222885524656,6.165126356924852,6.012738132613691,5.85880863205245,5.7053991524775025,5.554857924983656,5.409771302781305,5.272885010344755,5.146991190907552,5.03477874387941,4.938647447305872,4.8604908938183895,4.80145949103243,4.761722553109143,4.740270250607933,4.734968918623298,4.742996987325901,4.761336419677615,4.787190981668237,4.818311564431616,4.8532174348142085,4.8913077535153215,4.932862111151966,4.978932643002691,5.031134121986967,5.091342907399503,5.161321137335792,5.242289004631531,5.334484845663015,5.436941568928736,5.547710496748168,5.664184235511376,5.783357920509535,5.902046181553647,6.017092339466086,6.125602178034202,6.225192855596025,6.314219779591802,6.391948738930194,6.458649100755947,6.51559192809538,6.564944229655722,6.609557575696781,6.652656577317007,6.697440691517194,6.746625156194639,6.802056093465325,6.8646360036415635,5.586672956572552,5.657310494191146,5.707753639101652,5.73772563819518,5.748109921169657,5.740936182589992,5.7189562716027895,5.685125488077387,5.642168205091851,5.592253653132436,5.53679456688849,5.476374306827757,5.410801679073093,5.339286552034765,5.2607229586927495,5.1740593423491115,5.078728064108786,4.975057598462273,4.864355508232654,4.748660985266467,4.630499818444913,4.512694983620957,4.398208024265235,4.2899772061290244,4.190714891741552,4.102680166644134,4.027462685448508,3.9658069729584624,3.917498757162885,3.8813283424691396,3.8551406152478638,3.8359765903585465,3.8203068224095875,3.804351867927563,3.78447882317689,3.7576540694137837,3.7218441655461882,3.676097986253575,3.62040339461513,3.555492633634322,3.4826370629107295,3.4034526025616127,3.319729058157094,3.233289932421146,3.1458845075681987,3.05911073812557,2.9743655400441247,2.892818087369027,2.8154014487914845,2.7428180763093124],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[5.915544456967698],"y":[3.7145500599253864],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.1740157591912891,-0.25194383784616436,-0.3446690851633468,-0.452322208318499,-0.5725242287497841,-0.6999932896857197,-0.8267505709412588,-0.9429271305674531,-1.0380502649194354,-1.1025863426788463,-1.129457826079165,-1.1152478628914806,-1.0608580929425395,-0.9714845971803259,-0.8559042586301864,-0.7251945590585109,-0.591115837282442,-0.4644141361439421,-0.3533163470978802,-0.2625243621168307,-0.19288306559909474,-0.14175133676414475,-0.10397419499886718,-0.07324466580228028,-0.04357680866744029,-0.010599526778178325,0.027573813763545174,0.07005169949349976,0.11347624035979931,0.15284315947789118,0.18263090506666368,0.19805216845591145,0.19625214528774299,0.1771115202822895,0.1434699401106155,0.10073992167535752,0.05589873010912991,0.016079866072852778,-0.012846871713838387,-0.027419058887886927,-0.027229406237562648,-0.014952886950230337,0.00425058350511609,0.02383914823590777,0.037279394558901224,0.03944947310189778,0.02777860843459251,0.002898939270941703,-0.03134914504201003,-0.06862032155111958],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-2.5442721359069838,-2.4249646989415212,-2.2828957703782238,-2.1241197337893567,-1.955887151382971,-1.7861633467715305,-1.6230250502002193,-1.4739958490519218,-1.3453932401276525,-1.241762838858314,-1.1654680186210375,-1.1164865730914468,-1.0924418822659099,-1.0888675551148785,-1.0996753174534546,-1.117769866256047,-1.1357372836051078,-1.1465540939074996,-1.1442609796869636,-1.1244858257751038,-1.0847505645770035,-1.024539450968779,-0.9451362366802614,-0.8492660655545912,-0.7406013187618627,-0.6232059973005326,-0.5009985589239598,-0.37730784543342466,-0.25458173341075063,-0.13428564852507074,-0.016999493179833236,0.09733958584326563,0.2091343118922444,0.3187732272975754,0.42627151329717994,0.5309743871785528,0.6313719835919049,0.7250644571884964,0.8088989844951856,0.8792662193440713,0.9325182948806425,0.9654520391165514,0.9757910001451338,0.9625996156688028,0.9265724877605078,0.8701599348819326,0.7975152991547183,0.7142732552626302,0.6271068860425506,0.5429617677271074],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.284911781105562,1.2203685896655043,1.1505940825649499,1.0765761419152755,0.9989098809216626,0.9179687233440845,0.8341063686687875,0.7478624610083449,0.6601445699196173,0.5723619728840328,0.48649247236058635,0.40507157455552756,0.33110306055500827,0.26790039286055944,0.21887855163183678,0.18732484144455874,0.17617716587003462,0.18774922560935048,0.22335402161245899,0.2829892455678342,0.36515297005619707,0.4668000621471988,0.5834390546799497,0.7093587083418005,0.8379631773200071,0.9621855915416034,1.0749429097369014,1.1695907936307768,1.2403364436656763,1.282569942779772,1.2930840674675665,1.2702266112800946,1.2140579428227636,1.1264171790246482,1.0108681462663633,0.8725297584910068,0.7176826757137958,0.5532028758598682,0.38599987831458016,0.22251431920628317,0.06830472656389519,-0.07225352871918145,-0.19614325458519555,-0.3017510977761012,-0.38879138262411905,-0.45812585822084084,-0.5115056322044791,-0.5512676865688837,-0.5800211475942756,-0.6003580173648175],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.657611378100642,-1.4656279293419154,-1.268724796780245,-1.0742382842671971,-0.8872560962942768,-0.710081433222879,-0.5423678711277744,-0.3818781506178111,-0.2256725297587165,-0.07143135488058555,0.08141406039382987,0.23102102082563475,0.37311060235597565,0.5015902124038909,0.6096788657045654,0.6912677591491663,0.7421914470695209,0.7611368328169842,0.7500030369649917,0.713586404660491,0.6586575475255085,0.5926550493998863,0.5223067720863074,0.45250212615589425,0.3856746901838555,0.32182941454058694,0.2591921317925615,0.19530848758355362,0.12831059501134834,0.05802868384754989,-0.013338153976237055,-0.08116884879634678,-0.13901071792522623,-0.1796899176895831,-0.19668597960324374,-0.18545586528110858,-0.14446477790172274,-0.07568051168945322,0.015641483843627735,0.12182975089337966,0.23411591733257087,0.34409533712617657,0.44499838808776127,0.5324939295447508,0.6048635971333947,0.6625396131871838,0.7071529555995945,0.7403557593460043,0.7627180824914241,0.7729616537366316],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.1826295373744378,-1.1763941509512623,-1.176650566073951,-1.18096664514773,-1.1863316279337675,-1.1893909256893163,-1.1867402648565446,-1.1752464399405411,-1.1523570852056206,-1.1163619118244585,-1.0665729064875402,-1.0034005144058136,-0.9283157019431374,-0.8437024246377267,-0.7526195770025461,-0.6585041215290953,-0.5648535732520276,-0.4748955932142426,-0.3912554984005633,-0.31570619325367144,-0.24904086840352235,-0.19107642323170781,-0.14078024605078132,-0.09649881509963798,-0.05625510507268083,-0.018074608377931844,0.01970202319602099,0.058157762385464995,0.09761813126720009,0.13756535203391634,0.17665005379847043,0.21284996167981288,0.2438275125648407,0.26735039989238696,0.2816876605945158,0.2859306945947703,0.2801440996759715,0.26532884769160703,0.24325011457346324,0.21614865389164983,0.18636439962239448,0.15591707366041163,0.12609981370186785,0.09714656292584611,0.06803131488068659,0.03644733873628936,-0.001001784102661718,-0.04839175828530462,-0.10995563507789541,-0.1896555216633966],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[6.184732534053777,6.117070841836798,6.04598470131922,5.971973254041631,5.89569963889174,5.8180019783243395,5.73989749480339,5.662576916791322,5.587385995409042,5.515790797748399,5.449323595595962,5.389506785482738,5.337753537345662,5.295245954500293,5.262794566957911,5.240686959570309,5.228546049905443,5.22532684668071,5.22953887639039,5.239506384475378,5.253591944426224,5.270373894937296,5.288772555356667,5.308122702465235,5.328191630401677,5.349143518786639,5.371452171604988,5.395765850605045,5.422730237636328,5.452778673795082,5.485907555350123,5.521547202830074,5.558646060860566,5.595811775753826,5.631436870420612,5.663818731055677,5.69129490067763,5.712395933871579,5.7259963715021405,5.731446006406218,5.728668225872712,5.718216153194623,5.701280596317893,5.679646576027022,5.655597794550709,5.631771222920401,5.610967356157333,5.595925247404899,5.589064079650803,5.592183698993074,4.401907018593774,4.46900985813848,4.525545676274649,4.5712330251915905,4.6064334583519315,4.632169690884214,4.649882304487544,4.661123097416409,4.667301522927197,4.669495565400596,4.668331316373074,4.663932869319203,4.655942051257701,4.643605647664299,4.625925770965301,4.601866548757276,4.570607181544452,4.531803684211383,4.485680808743269,4.432939905823349,4.3746621405438955,4.312236560183756,4.247285265115821,4.18153625992962,4.1166668756180504,4.054153019551975,3.995139789588581,3.940343895183274,3.889994869990743,3.843819424365655,3.8010713100353826,3.7606074183278797,3.721009109271561,3.680745592522708,3.6383732841210725,3.592760513698559,3.5432796732594922,3.4898270605644846,3.4327286749532986,3.3726275439534503,3.310372755559327,3.2469197764559126,3.183247346530214,3.120292940692842,3.058906486456977,2.9998205833024354,2.943634702063706,2.890810564753464,2.841675956812484,2.7964344764374323],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[2.745669727375028],"y":[2.923531982028244],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.1749116488411414,0.1829919947867516,0.20338411173763493,0.2336515000161333,0.2708230549997247,0.31172728071300027,0.35332792713519157,0.3930209197721616,0.4288586765775046,0.45967838693305046,0.4851241429376293,0.5055671942114968,0.521942154913367,0.5355279675685679,0.5477094259676861,0.5597572254961677,0.5726599524410994,0.5870113064604983,0.602947239359274,0.6201663222181848,0.6380314419899193,0.6557270542818439,0.6724373679679977,0.6875065460345158,0.7005553432612035,0.7115869886120337,0.7210524958561241,0.729811115753554,0.7389870646576476,0.7497435601178268,0.7630062108244615,0.7792033167364885,0.7980999238244578,0.8187157337059775,0.8393340116822414,0.8576113581000686,0.8707500426507268,0.8757224860933472,0.8695592913659517,0.8496689460332946,0.8141473535145132,0.7620367285124243,0.6935002423004415,0.6098904024832424,0.5137041791367377,0.4084345758309253,0.2983446995703448,0.18819939113256,0.08286559948454074,-0.013412719019401635],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.2595305163491914,-1.226989646326241,-1.190480629654555,-1.1530788132020398,-1.1160690860377458,-1.0788304149592536,-1.0393101702313425,-0.9949515895477891,-0.9438232538122018,-0.8856461168582209,-0.822434387323378,-0.7585569628791333,-0.700165341969575,-0.6540895974650636,-0.6264396488768995,-0.6212326927788485,-0.6393747047749387,-0.678200575174847,-0.731657512174283,-0.7911912463838311,-0.8471803780867694,-0.8906139898773489,-0.9146540655330735,-0.9157491756461453,-0.8940736650385563,-0.8532578981611547,-0.79948027483125,-0.740097485469376,-0.6821238309723614,-0.6308946994967459,-0.5891913755328915,-0.5570039765793313,-0.5319590524481463,-0.5102243658331176,-0.48760368159187717,-0.4605407210886756,-0.4269842199176397,-0.38689506786129857,-0.3421015344297068,-0.29557036798620717,-0.2503263473468579,-0.20832912251460745,-0.16962144356449788,-0.13199546290739286,-0.09129911150914971,-0.04235164134582492,0.019707752918283084,0.09792059726742919,0.19226533627630532,0.29910745358514035],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.3590221908941618,1.3485944511340986,1.3298204813020154,1.2966971819602122,1.2439922378150712,1.1684472207726047,1.0695372950837374,0.9496387871533974,0.8135897335897674,0.6677630301751482,0.5188769527198648,0.3728203461670707,0.23375833441726107,0.10371204732533912,-0.017310679542306973,-0.13069079260021238,-0.23825470105025554,-0.3412229815863801,-0.43928838756964605,-0.5301203382334282,-0.6094526370899959,-0.6717572468445946,-0.7113730881114284,-0.7238522423278804,-0.7072249937789252,-0.6628708192508672,-0.5957873199285986,-0.5141908545698337,-0.4285024366765926,-0.3499030801702303,-0.28873529103739015,-0.25300660707830325,-0.24720258390711258,-0.2716779526454016,-0.3227106392168748,-0.3931750073963234,-0.47395027283428526,-0.5557431113419895,-0.6306961859828473,-0.6934889510732445,-0.7417871895981873,-0.7760297463109227,-0.7986737757512783,-0.8131235647351751,-0.8226193109719997,-0.8293498042958491,-0.833979842123409,-0.8356684745567238,-0.8325814749396048,-0.8228314433279795],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.7672737154843764,-0.7357994013384431,-0.7187767908311021,-0.7222370476056502,-0.7472655467693612,-0.7898430221223172,-0.841784341025448,-0.8925585452281539,-0.931573406238501,-0.9504053287958432,-0.9444744714743649,-0.9137998237131868,-0.8626863930318813,-0.7984437116397615,-0.7294518127654726,-0.663025428779364,-0.6035625416962515,-0.551569614061198,-0.5039417519144407,-0.45517023056626416,-0.399120577185509,-0.3309741083806203,-0.24887451344207528,-0.1548872887387593,-0.055009102961435546,0.041972890208073266,0.12650250188347562,0.1905520010336692,0.22967041531938237,0.24431447733756173,0.24013988258644103,0.22715867601891082,0.21792139073323064,0.22509409609423053,0.25893498356670724,0.325215805694042,0.4241409088136369,0.5504720971572032,0.6947009768388843,0.8449832430409867,0.9893953443570102,1.1180087235855507,1.2243341705453712,1.305853712321,1.363589206815205,1.4008989565401835,1.4218877015773683,1.4299083781750384,1.4264452566799741,1.4103967221831402],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.29308601626888386,-0.3490521235888327,-0.41234911307883093,-0.48184236068171027,-0.5560979385135912,-0.6334221157769613,-0.7119131630912553,-0.7895239644649761,-0.8641330843463909,-0.9336211214879221,-0.9959484706368474,-1.0492300639340393,-1.091802320005125,-1.122277416104104,-1.1395801225825717,-1.1429627826358049,-1.131996592787167,-1.1065654680220998,-1.0668867102932744,-1.0135210713401706,-0.9473623115438964,-0.8696119845135706,-0.7817463017043682,-0.6854826050489516,-0.5827465774076146,-0.4756129654506794,-0.36623153444840223,-0.2567749942308315,-0.14941712862008816,-0.04634491199994645,0.050196225586761845,0.13790641927313624,0.21459078748719929,0.2783578252586773,0.32781108399199077,0.36222037234252297,0.3815229139069299,0.3861745817037814,0.37700925342700076,0.3551273742786455,0.3218117750286107,0.2784690045251865,0.2265944736908897,0.1677595548471379,0.10361848837444876,0.0359325620317521,-0.03339141878308238,-0.10225593098630648,-0.16843729590514012,-0.22996577440522192],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[6.508958126564162,6.408558844651116,6.299639203643293,6.182480511441747,6.05764607068696,5.926023274839881,5.788857500205727,5.647771826138925,5.504765524169902,5.362183581723069,5.222649664169403,5.088956401571277,4.96391036213817,4.850135229507676,4.74984606287787,4.664620048804745,4.595215467522117,4.54164539103693,4.503585668592251,4.4807564290363775,4.473128218036828,4.480927698455155,4.504446189252032,4.543680281036149,4.597937178996509,4.665863172313989,4.7458072002202805,4.836083676461141,4.935051565208114,5.041007339536925,5.151929189928936,5.265287745728499,5.378161278290685,5.4874084954815014,5.589779646680886,5.682002784024148,5.760923644972414,5.823739557521482,5.868283727901077,5.893301359150439,5.898673371788739,5.885557348672539,5.856426106125573,5.814992474234103,5.76601583996399,5.714993421202607,5.667748482576115,5.6299386026950815,5.606501391924936,5.601030190599446,4.284351235369802,4.386019278007182,4.468420844199696,4.531031467470775,4.574718745974307,4.601785680792973,4.615418117154045,4.618989241145032,4.615492928394624,4.607132459148087,4.595073155288467,4.579360668994705,4.559001633080164,4.532198872634271,4.4967278127686825,4.45043280430625,4.391811262020639,4.3205818893229075,4.237796624525191,4.145497098546789,4.0463930759081865,3.9436458660212845,3.840666601096081,3.7407788927879295,3.646868437851495,3.5611406094296543,3.4850045896021604,3.4190645799250117,3.363165863031277,3.316423654322972,3.2772116753915057,3.2431722072817477,3.211320383587341,3.1782914831477043,3.1407519903042207,3.0959642212677023,3.042334071598776,2.9794953397843256,2.9080729023778185,2.829400641500897,2.7452498357473916,2.6575926144014472,2.5684126235585367,2.4795657647388394,2.3926877801191893,2.3091420461160923,2.229999512393312,2.156042638090863,2.0877859000075074,2.025506582168317],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[2.4355048520970453],"y":[3.043692509144023],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.033703400273556366,0.10166876604508479,0.150952405942858,0.17941760335959472,0.18638609899212166,0.17272384321486972,0.14078332701945678,0.09419802887668771,0.037540431859279466,-0.024128824180696062,-0.08577861555882771,-0.1429387100607742,-0.19218549492601877,-0.23152231229439824,-0.2606004335578157,-0.2807382841624333,-0.29471589627369443,-0.30638205764075244,-0.3201291312940372,-0.3402188009542516,-0.3699986454723353,-0.41110236257983523,-0.46306491809314954,-0.5238549919807701,-0.5907631585926123,-0.660515638708939,-0.7288287259981479,-0.7903332359477626,-0.8389353679807591,-0.8685448547611094,-0.8740788357510879,-0.8522965272636074,-0.8019152515811908,-0.7234234226602909,-0.6187085282298863,-0.49051318272632494,-0.3424147398845423,-0.17924653305122518,-0.007250058025867645,0.16607646245050733,0.3323516565796385,0.48282837330342243,0.608986121975849,0.7031456623957015,0.7590741193543997,0.7725745570591593,0.742082261124239,0.6692982219157932,0.5593549148957495,0.41955380560995215],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.24678034503052204,0.30034390179707493,0.33827584168066416,0.36535737687030356,0.38729953284868857,0.40913338991394244,0.4338964150298761,0.4618430020742179,0.4903020615339102,0.5141819598462871,0.5270043564011144,0.5222531176343275,0.49476737329692244,0.4418966702735061,0.3641705582963011,0.26530629536804406,0.15150332870633432,0.030495002806989024,-0.08911991995643365,-0.19863119680540686,-0.2899887143786102,-0.35634493201103756,-0.3925746827621439,-0.39615358905405695,-0.3677252368046271,-0.3105666722273225,-0.2292698943317769,-0.12849290617052003,-0.012065806878304122,0.11738349245402874,0.25820173670646285,0.409156448794472,0.5690091335771931,0.7360285866563739,0.9075508590633287,1.0797554074371507,1.2470648065133703,1.4014078306495186,1.5322219093645921,1.6272327120076067,1.6738324089863914,1.6608069518858566,1.5801234640184225,1.4284893904557108,1.2084371130861786,0.9287662917398615,0.6042805132192538,0.25486171431351967,-0.09619143690270926,-0.424739618874886],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.6004521983657298,-1.6342531016781436,-1.654380960313804,-1.6683674323584958,-1.6847971964402042,-1.709797620093513,-1.7441052409964024,-1.7815648016301278,-1.8095534751471105,-1.8113285607182508,-1.7697954068039914,-1.671808003893015,-1.5119407372534688,-1.294745038686291,-1.0348046066085739,-0.7543467848223806,-0.4787218474518272,-0.23154415262883768,-0.031406341770859006,0.11039403824866789,0.19083227679326775,0.2143780737444263,0.19098200085970096,0.13382188541704576,0.05669161063128292,-0.02784841408235017,-0.10916039145385936,-0.17855473737918037,-0.2287916714762505,-0.2533734119906273,-0.24607363688720715,-0.20098445421707567,-0.11312345719842981,0.020304217766077937,0.1983076137269909,0.4147175593352724,0.6571984159858213,0.9072018491279237,1.1414909615329507,1.3350893880882315,1.4650809073622988,1.514440363735122,1.475024391137045,1.3490176689584916,1.1484872681153144,0.8931630060042209,0.6070233808020336,0.31458719474659613,0.037347261639805396,-0.2098367156893972],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.8940902204673655,0.770889852692928,0.6661747872810628,0.5811430143383856,0.5110771087921439,0.4482718108168178,0.38546945580421377,0.31848499996656165,0.24711530270940152,0.1741709409904113,0.1032423649192532,0.036308891775137186,-0.027672892461135357,-0.09250760478435649,-0.16286056511494607,-0.2414672923086063,-0.32661397625416655,-0.41099804456401146,-0.4825739899970984,-0.5272304527952838,-0.5324629273378297,-0.4908502214870476,-0.40213575244763633,-0.2732443491505224,-0.1165290590462339,0.053541894592892825,0.2239739925641009,0.3854416765972948,0.532609525047413,0.662926096893665,0.7748284040160844,0.8661526579675687,0.9332149225637532,0.9715013978534668,0.9778718282922421,0.9532194302479406,0.9036870708111167,0.8397229447046706,0.7736126345536074,0.7161523834331187,0.6735185150638885,0.6454616022142461,0.625554832741932,0.6035063913674139,0.5687874028173734,0.5143298312336162,0.43901153592548336,0.3480867804124135,0.251458160624072,0.16044644119553642],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.38214929691086663,-0.44274728844697875,-0.4645848496778878,-0.4566250628365542,-0.431098448423377,-0.40148389471019175,-0.3803187735998055,-0.3772522516000686,-0.39770590288392704,-0.4423798813403298,-0.5076666882925294,-0.5868445170447039,-0.6717580065954918,-0.7545904399457279,-0.8293097169852315,-0.8924351579542642,-0.9429321315297816,-0.9815287104594521,-1.009912612597446,-1.0297406309472021,-1.0417863451193627,-1.045683458210452,-1.0398701381839164,-1.0210419299068398,-0.9842604605758987,-0.9238681383052163,-0.8348518608825866,-0.7143309660765362,-0.5627532262912149,-0.3844622417846151,-0.18745549559004338,0.017543302015595508,0.21837669380655977,0.40304355582855245,0.5613565643817265,0.6863275727057547,0.7748560250695928,0.827632762980988,0.848480537192899,0.8433037514541377,0.8188709999858045,0.7816772955957589,0.7370993734768646,0.6889798072449145,0.6396757678295144,0.5905115969377055,0.5425040415277432,0.4971875425458553,0.45704222478948314,0.42479253906415304],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[7.25505299557851,7.137551682383661,7.003065586816941,6.850757197833216,6.680245524148064,6.491760340924872,6.286298647605154,6.065765746217712,5.83307632485728,5.592184327451336,5.348006307706342,5.1062047928424725,4.872810809967363,4.653694310285095,4.453943872902459,4.277295204125445,4.1258701171820285,4.000820440853111,3.9037247422528303,3.8373529148411953,3.8052959931501005,3.810574933351678,3.8541959386697613,3.934633645627583,4.047576706081331,4.186818119196312,4.346050724332167,4.52015823126421,4.705617420523785,4.899987273532085,5.100712445487534,5.304208480937758,5.506177597643976,5.702026516161326,5.886748949195261,6.054451127081881,6.198242314874243,6.310870077358628,6.385734591063956,6.417950774314065,6.405252403102528,6.348620080091091,6.252572137625074,6.125090798253921,5.977178017209505,5.822060393541326,5.67410182130605,5.547534687975744,5.455024839002489,5.405759381958511,4.277924512377107,4.46449311228622,4.616210139485795,4.730391078807945,4.808057387340481,4.854646701482398,4.878434025762911,4.888301415636657,4.89192192709032,4.894461110972527,4.897822756403338,4.900440855165586,4.89760854833719,4.882326422378506,4.846633699544046,4.783344583071062,4.688041952330253,4.560869038892449,4.406431335216315,4.232053896327058,4.0464433215186,3.8590580262815575,3.679628066453743,3.517018185795305,3.3779759398107783,3.266404455070053,3.1833198578428874,3.1274012229332975,3.095792161838991,3.0846330951460037,3.08922608254278,3.1039919010735906,3.1220928447985687,3.1352892952286235,3.1346636420994924,3.1124180221880318,3.0640731210223864,2.988994020737389,2.8895771002806843,2.7702234564161756,2.6363705655647864,2.4936984627503653,2.3475533670792377,2.202582875946002,2.0625503393526308,1.9302858513170351,1.8077314225398453,1.6960435364851105,1.5957241282641816,1.5067590267691822],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.5153938687938275],"y":[7.49092917848877],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.3284140462138216,-0.36547672694925,-0.4353964440565486,-0.530639203437277,-0.6380937848150042,-0.7414094557353612,-0.824007505756843,-0.8722040669042961,-0.8778593301554062,-0.8400555980115594,-0.7654843372487659,-0.6674533005866257,-0.563661157704991,-0.47308012285034806,-0.4123964387801067,-0.39246008419028977,-0.41518803041515984,-0.4725518111725563,-0.5489558326844688,-0.6250347914017802,-0.6820753482793565,-0.7067908667568688,-0.6942768774222252,-0.6466384072785012,-0.5700894605483353,-0.4728445029194921,-0.3636966207461225,-0.2504892269194883,-0.1388531641736832,-0.031767608160154115,0.06962571382303073,0.16499361486581676,0.25521718285230494,0.3424934813840218,0.4297222571125726,0.5196514309403422,0.6134338903822512,0.7091067930806445,0.8011102330498401,0.8807398804388971,0.9370930751934146,0.9585241621449403,0.934381255423143,0.8567063503857528,0.7217179308370947,0.5310956770447324,0.29331434691293246,0.025375017736763983,-0.24767811876623713,-0.5007019741156902],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.029464620887478477,0.13114222463016012,0.23637453049896728,0.2841785878731282,0.27967333621853374,0.23388061956332074,0.16131224355030538,0.07697121700266463,-0.006568575528215881,-0.08138010546157082,-0.14524789722039788,-0.20139526579311706,-0.25698883613523105,-0.3208043514087282,-0.4006243985358968,-0.5010116033848164,-0.6220155548252371,-0.7586776711222964,-0.9010375727001958,-1.0353682071523598,-1.1466778801105204,-1.222092487885614,-1.25345060034575,-1.2372711999844443,-1.1738442870636885,-1.066378169840599,-0.9201607774843901,-0.7416346550435047,-0.5375276218144952,-0.3141797276163205,-0.0771330145202318,0.16879335033362386,0.4187404690617986,0.6669576063524585,0.906246494502347,1.127871715481454,1.3220595975403642,1.4791543566035679,1.5913962715954397,1.6541227953226398,1.6650438560214316,1.6232420908034841,1.5285629769258449,1.3814111271424105,1.18304771214802,0.936538263921,0.6485055441427482,0.33171151771595353,0.0058555482951834215,-0.3083273195238454],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.4324843258978617,-1.3511959878643611,-1.2273999187498708,-1.0591471103473664,-0.8487768040937473,-0.6043051892401383,-0.3399306179199849,-0.07534902122464504,0.16616843492605726,0.3606927522315332,0.4870565262895796,0.530138368405729,0.48338032749889015,0.35006846555699767,0.143196541762741,-0.11591054508912824,-0.39977225037613273,-0.6781211971768828,-0.9226993136302686,-1.111412670287224,-1.2311048918559346,-1.2790698889308127,-1.262323697249896,-1.1936571117483323,-1.087382317195225,-0.9555603202461991,-0.8053414344501097,-0.6384084287312852,-0.4524175232123613,-0.24390440444009687,-0.011869536795233615,0.2393463474955047,0.4993827900380188,0.7532733235211387,0.9850178066185848,1.182624584858159,1.339729715542378,1.453350785691327,1.5211698165342817,1.540163904091503,1.5083727650488281,1.426403364399218,1.2976068493310486,1.1274769128902076,0.9228997754415393,0.6918178665239247,0.4437181818909491,0.19110830895924105,-0.049720455155679154,-0.2619200983127333],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.7739370962191368,0.7538374766846057,0.669874913640321,0.5298338683043196,0.35747179484505254,0.1857106581425948,0.04767486222358086,-0.0321070355629296,-0.04410314596820475,0.0037987823247832564,0.08837911610261939,0.1770518119451049,0.23609459776240416,0.23899021542289156,0.17276125737935388,0.040780726712539295,-0.13848092357664965,-0.3365037319350766,-0.5222877664149391,-0.6698600927563483,-0.7634451387843876,-0.7988243138974279,-0.7819509178843357,-0.7273487968240029,-0.6550323977884299,-0.5838461899119529,-0.5239520947620986,-0.47306034589880336,-0.41724738453480087,-0.3357261637316035,-0.2080089668506827,-0.02129928474191356,0.224081228460829,0.5127293091009922,0.8162819356696115,1.0991757931247217,1.326516544734156,1.4721030207476962,1.524707461797862,1.4905695237650969,1.3908966424321836,1.2556527686298253,1.1154082714517053,0.9932925472618914,0.899168901972401,0.827674075911899,0.7608529166564759,0.6749802803524698,0.5491503651579752,0.37170926498420553],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.1976556973306636,1.1273195183893958,1.0304191959738982,0.9154142297631616,0.7973621368479352,0.6885553998680913,0.5906207425833783,0.4926024874678969,0.3761491654237692,0.22489455113520895,0.03281269919173346,-0.19294554415270415,-0.4359276738333533,-0.6782576749426426,-0.9075981144279242,-1.1190144749825075,-1.3107938106659325,-1.4777910179458074,-1.607706199312886,-1.6827375325584688,-1.6866382690378323,-1.6140729868281465,-1.4764587781880096,-1.2996487134694839,-1.1150994206164855,-0.9476614651860826,-0.8058054492926154,-0.679765852431752,-0.5480343719365419,-0.38848105632397,-0.18846298652976956,0.050984095082002856,0.3183491866237862,0.5985779668224072,0.8786799086773601,1.1486305314948564,1.3982481372342255,1.6133533590487505,1.7751591635933244,1.8640151828781562,1.8649231022227706,1.7739758667989887,1.60187576956659,1.3712828473380152,1.1086231636875206,0.8346296081388807,0.5591371822648631,0.28367748361990924,0.009165154300023959,-0.25976222743755106],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[11.883401498927746,11.573254841945296,11.20851176446407,10.786082907901966,10.304972518114692,9.767093835999152,9.178096534615705,8.54807856255988,7.891992991676303,7.229498674349257,6.583962127135022,5.980333264421032,5.441745503372584,4.985006319874859,4.61572525905208,4.324701015302489,4.0884432370181,3.879122547206477,3.680547872167468,3.49606637484856,3.3446804911744037,3.2489617573019305,3.2243070789518797,3.275593479788058,3.3948632582116396,3.5652703276372018,3.7718672056901674,4.009624090005277,4.283846949960568,4.602682166530621,4.965807435360566,5.3597719379391675,5.7663124255336555,6.1708233373105426,6.56318676148459,6.9333898929280195,7.271310212612353,7.568840826375143,7.815442774946349,7.9913773028052795,8.069261563787231,8.02238630996145,7.834103965504324,7.504568878390485,7.0530015235923145,6.515458291968082,5.939797516475663,5.38101865278652,4.898686620375203,4.549773016916674,3.768871669994112,4.394021480645078,4.954817275497169,5.439007237292357,5.838324794308706,6.159411659898872,6.42029596458346,6.639371407537654,6.825820541689008,6.974552452658624,7.067103955370733,7.078376513709,6.987396559801369,6.788468859066758,6.49519806109064,6.131165547477493,5.7210286055265716,5.289115433043287,4.857291799771986,4.439977187823161,4.044368927451473,3.6779138832482126,3.355840906463056,3.097496230288278,2.916404428502661,2.8134285552582767,2.7770841475352155,2.790642683167867,2.841283824678819,2.9231413925707246,3.035049989153327,3.1774241653316277,3.3437057301449995,3.5112149916757973,3.6399984447713774,3.683567199458939,3.6071713286401597,3.3969468560224847,3.0582657523272827,2.610462240490886,2.0807885771788714,1.4990946189779573,0.8938816623496026,0.28982384317906007,-0.2934469708099652,-0.841610836022979,-1.345306580370126,-1.7994290549558434,-2.202282143263047,-2.5547265688445977],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.035550221532578],"y":[8.35378853998293],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.1213017642923013,1.942272951541296,1.7607853755040621,1.5815211043416717,1.4074132411665716,1.2396640031346036,1.0779473187872095,0.9207604765633141,0.7658751652520884,0.6108300178988083,0.4534054956682245,0.2920279581757892,0.12606271010437498,-0.04402529316614068,-0.21664105243212162,-0.3891314512821702,-0.5579170200244383,-0.7187790477172877,-0.8673632349443494,-0.9995809060157976,-1.1117377478127426,-1.2003212478565792,-1.2617060157346094,-1.292111358614766,-1.2874508346418883,-1.2435846264411257,-1.1569914909318584,-1.025430596406162,-0.8487344100305425,-0.6299756456694393,-0.3771698574031276,-0.10382915838627735,0.17388548987944535,0.4406485449954164,0.6849692576046266,0.9015178944903527,1.0904383114401957,1.25393737477738,1.3926370435673627,1.503075225931415,1.5775387580118712,1.6046861375201478,1.5704203721319103,1.4593476125741163,1.257413249511162,0.9556528501880255,0.5550565163037904,0.07264228660797767,-0.4565495439442512,-0.9913914711430196],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.8144245532975211,1.001543525672909,1.1442372774467438,1.2398389188775303,1.2744062628669552,1.2301335449665916,1.095361619133101,0.8731713988517698,0.5850248640157615,0.26773320217134533,-0.03548853734159563,-0.2868916689423032,-0.46484123314162107,-0.5694246996836901,-0.6208976956409505,-0.6512607416801927,-0.6916112087000901,-0.7605405190528066,-0.8585483395674535,-0.9688411045303477,-1.0639249864689266,-1.115919282167785,-1.1067941606290463,-1.0347745664367025,-0.9153226953877805,-0.7746633000275626,-0.6385918369022743,-0.5224307333690498,-0.4256397670276283,-0.33278143490789813,-0.22029975763261123,-0.06659000184634856,0.13837989533469885,0.38805726387516515,0.6613908065500302,0.9313444031298475,1.173633313920437,1.3719036214483125,1.5188617381541394,1.614024847206458,1.6609972799193575,1.662126079240374,1.6126472365350466,1.4977821726731437,1.2939547678663272,0.9757711241113105,0.5278674557652479,-0.04204978904946355,-0.6962974582011716,-1.3753375583224898],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.9840034332082928,1.9813442778644934,1.9117306511076384,1.7744622077351035,1.5773591137334888,1.3356558384995638,1.06916279013789,0.7984399780771934,0.5409848113422675,0.30841515949523823,0.10533418492763458,-0.06992383000681435,-0.223013315715491,-0.36056423375407287,-0.48747690440273284,-0.6055273780720377,-0.7138967076987416,-0.8105832460420257,-0.8932293750264101,-0.9601008032325916,-1.0106090159124808,-1.04434245393004,-1.060032388011816,-1.0568238945588404,-1.0349564108457172,-0.994193936346556,-0.9314291484838704,-0.8397326257154003,-0.7096615909165317,-0.5329773748558009,-0.3082859476106963,-0.04521989061611387,0.23712147851892873,0.5147532197585508,0.7655254934041554,0.9771242707955999,1.1486508111177618,1.2853218767404857,1.3920958172000262,1.4694189845113286,1.5141718973527016,1.5204956754480978,1.478981818855821,1.3757156913733488,1.193282756143656,0.9143070155595874,0.5277708197641433,0.038187395328127316,-0.5287578411040337,-1.135857794256203],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.0220745847127082,-0.8903682867267141,-0.7337437078277421,-0.5642176045505648,-0.39714578832460656,-0.24802158444060884,-0.1295463512787982,-0.049692287796968326,-0.011146601189366834,-0.012096749240180227,-0.04792048366394264,-0.11310181316244261,-0.2026772678754596,-0.31272926614082897,-0.43981812462010916,-0.5796645300088286,-0.7257185918358293,-0.8682580760950387,-0.9945706233924323,-1.0907637123497502,-1.145177426846188,-1.1527615176524648,-1.1175110845254856,-1.049592134787955,-0.9600188062621058,-0.8581476582835323,-0.7514698317396105,-0.6444689457573838,-0.5373500379064875,-0.4260410564936161,-0.3044932048509622,-0.16743913187162363,-0.01046541139584456,0.1697666698385762,0.374735761178123,0.6036000240999301,0.8513245806854987,1.1060528042577449,1.3482196542421323,1.55229068279872,1.6915109985446914,1.7428368226821864,1.6906335983748657,1.5285896784638133,1.2592427835882325,0.8924266196373574,0.4440773656198034,-0.06383868636840218,-0.6038423109956286,-1.1475654116687948],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.17953134377399393,0.007118343473551558,0.18961651665708118,0.3612187250657054,0.51348184721765,0.637097191784532,0.7229560561477115,0.7633023656624475,0.7528136498238441,0.6894602282628395,0.5750221536374438,0.4151905815276645,0.21923899947162084,-0.0006871005643505068,-0.23055371964116933,-0.45553739985263975,-0.6610798180432507,-0.8341359184872412,-0.9648320989617545,-1.04786908545342,-1.0834572312120525,-1.077784052744103,-1.0418766109639352,-0.9875262155924911,-0.9226338915371086,-0.8495036269099066,-0.7658373402366321,-0.6662622631954522,-0.5444009164609684,-0.39577910044237896,-0.2216671892807427,-0.031104525518324877,0.16255436882906027,0.3467318016159613,0.5150046446734691,0.6720709828077536,0.8308391661545911,1.0022452240606303,1.1851952183233436,1.3618201979259568,1.5027421121967999,1.5754054857944868,1.5527480851540805,1.4204209907683423,1.1779146539232777,0.8370385045039381,0.4208007885706181,-0.03741813082335438,-0.49659187405157695,-0.9164616652744428],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[18.338065481744763,17.427615671766084,16.417416088487727,15.314346266669592,14.131239295945079,12.887686261920866,11.610414190349033,10.332968023486782,9.094391849782058,7.936615492508028,6.900349241934507,6.019524555368391,5.314751421396943,4.786940336256132,4.413144357826833,4.147638597404472,3.9320282966156146,3.718448064089602,3.4929510013171514,3.2760539397777237,3.101946373960347,2.9938601180304407,2.9593488796892826,3.001831963511977,3.11606858889696,3.282756326781617,3.4815572418422023,3.7070569264459867,3.9716959056203227,4.291780635037977,4.666937150514814,5.0761441392356526,5.498228455654141,5.926336384449383,6.360555550074437,6.792171443088367,7.2056939457578295,7.5890697725443514,7.927475476871721,8.195182254357563,8.366620651717986,8.425634938448406,8.355672721872622,8.125918341804226,7.70253432035509,7.07178966067408,6.25142602356157,5.291000342665118,4.274385793055321,3.3151812996124463,3.107659452193013,4.186558028721026,5.219185639111165,6.158336462449998,6.946806324758837,7.556395365172216,7.985256017671233,8.238498113646834,8.323438115594135,8.25969738170461,8.081521621768013,7.820586574725808,7.49481230500878,7.116557895132225,6.7031398412094,6.269521045280971,5.823543608736872,5.377473859490353,4.950743444044229,4.554252455990262,4.182838611307936,3.829427337239616,3.505278927036325,3.236444129571852,3.0437673064873065,2.9291425153662978,2.8783524198667463,2.87656332286926,2.920377208414964,3.0102576431327632,3.1423985267282357,3.317600976107925,3.5392277793343196,3.7935055210751942,4.03341221902894,4.183934530527716,4.169249629416374,3.935290302321866,3.4571568515507236,2.73804520897638,1.8035075280583799,0.6939290342417923,-0.5428279656997868,-1.8575464893554532,-3.2041362822354102,-4.542485271369539,-5.839915824302907,-7.071568354377181,-8.220038746668326,-9.274555360610885],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[5.143971561084619],"y":[8.298211828582026],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"11"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"18"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"25"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"32"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false],"title":"39"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true],"title":"46"}],"label":"i = 6","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Random
Choose the next point by uniformly sampling a point from the domain.

In [84]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=None,
    random_class=Models.UNIFORM,
    random_trials=10,
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client, acqf_n=0)
results["Random"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:24] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:24] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 09:43:24] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


### Comparison
Compare the acquisition methods from above by showing the max gold achieved against how many trials in the experiment.

In [85]:
max_gold = {"Method": [], "Trial": [], "Max Gold": []}
for k, v in results.items():
    max_gold["Method"].extend([k] * (len(v) + 1))
    max_gold["Trial"].extend([0] + (v.trial_index + 1).to_list())
    max_gold["Max Gold"].extend([0] + v["gold"].cummax().tolist())
render_plotly_html(px.line(max_gold, x="Trial", y="Max Gold", color="Method"))

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="7a8d0ccc-5175-428a-a5f1-70119c7cd06d" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("7a8d0ccc-5175-428a-a5f1-70119c7cd06d")) {                    Plotly.newPlot(                        "7a8d0ccc-5175-428a-a5f1-70119c7cd06d",                        [{"hovertemplate":"Method=PI\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"PI","line":{"color":"#636efa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"PI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,7.78026814236398,7.78026814236398,7.78026814236398,7.97083381305886,8.353438586358578,8.353817966113354,8.353817966113354],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=EI\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"EI","line":{"color":"#EF553B","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"EI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.909021517750929,7.691138525684522,8.331261799710944,8.348254087751911],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=UCB\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"UCB","line":{"color":"#00cc96","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"UCB","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,8.062511138469858,8.062511138469858,8.353042361423036,8.353042361423036,8.353042361423036,8.353604872575431,8.353772660864934],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=Thompson\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"Thompson","line":{"color":"#ab63fa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"Thompson","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,7.49092917848877,8.35378853998293,8.35378853998293],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=Random\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"Random","line":{"color":"#FFA15A","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"Random","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,5.057664805217066,5.091532753266253,5.703244208949001,5.776814007863983,5.776814007863983,5.776814007863983,5.776814007863983,5.776814007863983,6.01297425838335,6.01297425838335],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"Trial"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"Max Gold"}},"legend":{"title":{"text":"Method"},"tracegroupgap":0},"margin":{"t":60}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

## Hyperparameter Tuning

In [86]:
# Import moons and SVC from sklearn
from sklearn.datasets import make_moons
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

In [87]:
X, y_true = make_moons(n_samples=300, noise=1.0)
px.scatter(x=X[:, 0], y=X[:, 1], color=y_true)

In [88]:
results_svc: Dict[str, pd.DataFrame] = {}

### Ax Helper Functions

In [89]:
def evaluate_svc(parameterization: TParameterization) -> TEvaluationOutcome:
    _C = parameterization.get("C", 1.0)
    _gamma = parameterization.get("gamma", 1.0)
    svc = SVC(C=_C, gamma=_gamma).fit(X=X, y=y_true)
    y_pred = svc.predict(X=X)
    return {"accuracy": (accuracy_score(y_true=y_true, y_pred=y_pred), None)}


def create_svc_client(
    botorch_acqf_class,
    random_class=Models.SOBOL,
    random_trials: int = 3,
) -> AxClient:
    ax_client = AxClient(
        verbose_logging=False,
        random_seed=1,
        generation_strategy=create_generation_strategy(
            botorch_acqf_class=botorch_acqf_class,
            random_class=random_class,
            random_trials=random_trials,
        ),
    )
    ax_client.create_experiment(
        name="moons_dataset_svc",
        parameters=[
            {
                "name": "C",
                "type": "range",
                "bounds": [1e-9, 10],
                "value_type": "float",
                "log_scale": True,
            },
            {
                "name": "gamma",
                "type": "range",
                "bounds": [1e-6, 1e3],
                "value_type": "float",
                "log_scale": True,
            },
        ],
        objectives={"accuracy": ObjectiveProperties(minimize=False)},
    )
    return ax_client

### Probability of Improvement (PI)

In [90]:
ax_client = create_svc_client(botorch_acqf_class=ProbabilityOfImprovement)
for i in range(10):
    parameterization, trial_index = ax_client.get_next_trial()
    ax_client.complete_trial(
        trial_index=trial_index, raw_data=evaluate_svc(parameterization)
    )
results_svc["PI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:25] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:25] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='C', parameter_type=FLOAT, range=[1e-09, 10.0], log_scale=True), RangeParameter(name='gamma', parameter_type=FLOAT, range=[1e-06, 1000.0], log_scale=True)], parameter_constraints=[]).
[WARNING 08-11 09:43:28] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [91]:
model = cast(
    TorchModelBridge,
    not_none(ax_client.generation_strategy.model),
)
fig = interact_contour_plotly(model=model, metric_name="accuracy")
fig.update_layout(dict(width=None, autosize=True))
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="3d896191-dfd8-41b9-8633-ee3310dc3fa1" class="plotly-graph-div" style="height:450px; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("3d896191-dfd8-41b9-8633-ee3310dc3fa1")) {                    Plotly.newPlot(                        "3d896191-dfd8-41b9-8633-ee3310dc3fa1",                        [{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x","y":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"yaxis":"y","z":[[0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687],[0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303],[0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911],[0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357],[0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011],[0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554],[0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298],[0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475],[0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855],[0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989],[0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067],[0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081],[0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462],[0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415],[0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884],[0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991],[0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146],[0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343],[0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586],[0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768],[0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368],[0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978],[0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055],[0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823],[0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662],[0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555],[0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298],[0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687],[0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919],[0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651],[0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005],[0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517],[0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729],[0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771],[0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376],[1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599],[1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015],[0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121],[0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491],[0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972],[0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153],[0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327],[0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758],[0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354],[0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968],[0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849],[0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069],[0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238],[0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234],[0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x2","y":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"yaxis":"y2","z":[[0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983],[0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026],[0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545],[0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232],[0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695],[0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112],[0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273],[0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956],[0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747],[0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042],[0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163],[0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986],[0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475],[0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596],[0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933],[0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173],[0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252],[0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378],[0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456],[0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619],[0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595],[0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323],[0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684],[0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374],[0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286],[0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245],[0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789],[0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149],[0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204],[0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265],[0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473],[0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507],[0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754],[0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092],[0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372],[0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702],[0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108],[0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757],[0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798],[0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142],[0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385],[0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357],[0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132],[0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354],[0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231],[0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835],[0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845],[0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966],[0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992],[0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 0.97 (SEM: None)\u003cbr\u003eC: 0.0160084\u003cbr\u003egamma: 85.2516","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0234392\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0272673\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0229824\u003cbr\u003egamma: 690.262","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223817\u003cbr\u003egamma: 631.808","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223928\u003cbr\u003egamma: 633.153"],"visible":false,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],"xaxis":"x","y":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 0.97 (SEM: None)\u003cbr\u003eC: 0.0160084\u003cbr\u003egamma: 85.2516","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0234392\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0272673\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0229824\u003cbr\u003egamma: 690.262","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223817\u003cbr\u003egamma: 631.808","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223928\u003cbr\u003egamma: 633.153"],"visible":false,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],"xaxis":"x2","y":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],"yaxis":"y2","type":"scatter"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x","y":[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],"yaxis":"y","z":[[0.7825999309160263,0.7817688174220705,0.7809595144128343,0.7801754532937346,0.7794200579395778,0.7786967113067211,0.7780087204335573,0.7773592804424426,0.7767514382506865,0.776188056775596,0.775671780472028,0.7752050030641993,0.7747898383216179,0.7744280946787895,0.7741212544091469,0.773870457937605,0.7736764937183724,0.773539793922955,0.773460435987656,0.7734381498715952,0.7734723306869475,0.7735620561935729,0.7737061085095965,0.7739029992844799,0.7741509975154313,0.7744481591624361,0.7747923577297153,0.7751813150277268,0.7756126314039138,0.7760838148252795,0.77659230830422,0.7771355152738038,0.7777108226335012,0.7783156212958525,0.7789473241645226,0.7796033815616199,0.7802812941951828,0.7809786238155454,0.7816930017519327,0.7824221355488601,0.783163813937008,0.7839159103768798,0.7846763854075882,0.7854432880195352,0.7862147562504994,0.7869890171815688,0.7877643864841568,0.788539267643465,0.7893121509584601,0.7900816123946789],[0.7791559637444286,0.7782057241461113,0.7772791216893056,0.7763802104585884,0.7755130538820211,0.7746816836386519,0.7738900559887403,0.7731420062952051,0.7724412026589015,0.771791099724937,0.7711948938205637,0.7706554806455965,0.7701754167436399,0.7697568859293007,0.7694016717297552,0.7691111367203927,0.7688862094011508,0.7687273789852981,0.7686346981728372,0.7686077936761178,0.7686458839760484,0.7687478035323339,0.7689120324658518,0.7691367305861854,0.7694197745574396,0.7697587969802443,0.7701512262118976,0.7705943258407871,0.7710852328640725,0.7716209937765963,0.7721985979518557,0.7728150078714293,0.7734671859281248,0.774152117682944,0.7748668315915583,0.7756084153291507,0.776374028931811,0.7771609150382196,0.7779664065583529,0.7787879321184518,0.7796230196361609,0.78046929836954,0.7813244997616682,0.7821864573718875,0.7830531061482561,0.7839224812561508,0.7847927166374906,0.7856620434356669,0.7865287883845107,0.7873913722266282],[0.7755612046875043,0.7744806447697367,0.7734253528728785,0.7724000881223575,0.7714096452466597,0.7704588045834847,0.7695522780635919,0.7686946520978671,0.7678903285405567,0.7671434651319713,0.7664579170171881,0.7658371810720691,0.7652843448237983,0.7648020417135061,0.7643924143033781,0.7640570867792117,0.7637971477516852,0.7636131439364642,0.7635050848246184,0.7634724579763992,0.7635142541204066,0.7636290008505229,0.763814803411347,0.7640693908659104,0.7643901658526633,0.7647742561572345,0.7652185664348329,0.7657198286022541,0.7662746496523576,0.7668795559065364,0.767531032992014,0.7682255610939053,0.7689596452739409,0.7697298408595719,0.7705327740835405,0.771365158292682,0.7722238061459894,0.7731056382879375,0.7740076890171372,0.7749271094768218,0.7758611688771431,0.7768072542246098,0.7777628689859861,0.7787256310570887,0.7796932703452455,0.7806636262113273,0.7816346449562337,0.7826043774799445,0.7835709771905172,0.7845326981969258],[0.7718623059270656,0.7706410612165414,0.7694463935628939,0.7682838457596898,0.767159035034543,0.7660775932193596,0.7650451007920248,0.7640670158288773,0.763148599295066,0.7622948384859423,0.761510370784614,0.7607994101803887,0.7601656791596841,0.7596123485981022,0.7591419881227505,0.7587565290671752,0.7584572416184727,0.7582447270913604,0.7581189255115965,0.7580791379188812,0.7581240620783276,0.758251839683534,0.7584601126904693,0.7587460861651657,0.7591065949618925,0.7595381716542602,0.7600371133873698,0.7605995456647621,0.7612214814882771,0.7618988746942609,0.7626276667446884,0.7634038266134441,0.7642233837407978,0.7650824543045077,0.7659772612710614,0.7669041488465193,0.7678595920473313,0.7688402021632379,0.7698427288938092,0.7708640599146862,0.7719012185765144,0.7729513603661075,0.7740117686722617,0.7750798503040603,0.7761531311129334,0.7772292519758623,0.7783059653097435,0.7793811322089437,0.7804527202314758,0.7815188018050608],[0.7681194613695492,0.766748773735469,0.7654055076275009,0.7640960556586267,0.7628269397237039,0.7616047410584158,0.7604360212146433,0.7593272349707856,0.7582846367789403,0.7573141829775872,0.7564214326209984,0.7556114503302318,0.754888714977716,0.75425703819749,0.7537194965968279,0.7532783810912964,0.7529351659967157,0.7526904994421109,0.7525442154201747,0.7524953665017597,0.7525422750528251,0.7526825998320117,0.7529134142003125,0.7532312918756201,0.7536323961988919,0.7541125691913464,0.7546674171973562,0.7552923905435667,0.7559828553262368,0.7567341561054826,0.7575416688941157,0.7584008443538468,0.7593072415404207,0.7602565528695979,0.761244621212496,0.7622674501803551,0.7633212087359573,0.7644022312831171,0.76550701434812,0.7666322108886326,0.7677746231566762,0.7689311949123906,0.7700990036433933,0.7712752532986378,0.7724572679028978,0.7736424862843708,0.7748284580281202,0.7760128406656008,0.7771933980273302,0.7783679996226198],[0.7644066131624461,0.7628803037087047,0.7613816503171235,0.7599179368033685,0.7584966500663786,0.7571254009998493,0.7558118324120877,0.7545635146595495,0.7533878305168161,0.7522918517687283,0.7512822110645343,0.7503649736232054,0.7495455142848727,0.7488284059961017,0.7482173259238347,0.7477149848811532,0.7473230845710898,0.7470423053876852,0.7468723253575404,0.7468118685525154,0.7468587792714871,0.7470101167412799,0.7472622641805664,0.7476110458334412,0.7480518459277447,0.7485797242935467,0.7491895244132124,0.7498759708047873,0.7506337537401615,0.7514576002865521,0.7523423314908446,0.7532829061872415,0.7542744524046622,0.7553122876972169,0.7563919299389131,0.7575091002331482,0.7586597196075445,0.7598399011122763,0.7610459388301378,0.7622742951526504,0.7635215874908454,0.764784575383674,0.7660601487523825,0.7673453178360211,0.7686372051409045,0.7699330395532767,0.7712301526058247,0.772525976759172,0.7738180454610394,0.7751039946782909],[0.7608104380917559,0.7591260543073426,0.7574688295023149,0.7558469400227967,0.7542688589464538,0.7527432707000669,0.7512789679898937,0.7498847309337657,0.7485691892892454,0.7473406700088852,0.7462070340040997,0.7451755078668066,0.7442525181773246,0.7434435375932246,0.7427529527558381,0.7421839637650132,0.7417385233062466,0.741417320511525,0.7412198107012041,0.7411442879791892,0.7411879940064197,0.7413472537614713,0.7416176279844857,0.7419940722129353,0.7424710935286964,0.7430428979247321,0.743703523179915,0.7444469540201935,0.745267217979871,0.7461584616927069,0.7471150083387711,0.7481313976845871,0.7492024106291635,0.7503230804548164,0.7514886931201405,0.7526947789552756,0.7539370980509242,0.755211621490478,0.7565145103734776,0.7578420943311078,0.7591908509530387,0.76055738724286,0.761938423910599,0.7633307830095909,0.7647313791448358,0.7661372142326659,0.7675453755860294,0.7689530369414197,0.7703574619341902,0.7717560094669115],[0.7574276161041409,0.7555876707133791,0.7537735987160631,0.7519944149052549,0.7502595407713224,0.7485787178578799,0.746961898641737,0.7454191133693945,0.7439603122344476,0.7425951837986042,0.7413329527716008,0.7401821632167636,0.7391504567926845,0.738244359311351,0.7374690918284916,0.7368284235318137,0.736324581801008,0.7359582296125362,0.7357285127358465,0.7356331707551761,0.7356686990016452,0.7358305444995439,0.7361133183508335,0.7365110089109779,0.7370171834948664,0.7376251701232277,0.738328214265178,0.7391196083186486,0.7399927936365682,0.7409414363374398,0.7419594790704205,0.7430411714714629,0.7441810823579932,0.745374096844274,0.7466154015700893,0.7479004611526472,0.7492249888121361,0.750584913893493,0.7519763487160073,0.753395556834933,0.7548389244057198,0.7563029359171816,0.7577841551248499,0.7592792115925715,0.7607847928618755,0.762297641934694,0.7638145594903587,0.765332410070276,0.766848131353997,0.7683587456127995],[0.7543599151104028,0.7523730363067228,0.7504100163101179,0.7484805901925393,0.7465950156751773,0.7447639914999795,0.7429985497212734,0.7413099184986991,0.7397093524137892,0.7382079284193244,0.7368163076381854,0.7355444668201967,0.7344014087484856,0.7333948682393471,0.7325310385199496,0.7318143489843507,0.7312473256446319,0.7308305569209714,0.7305627706231158,0.7304410088064978,0.730460872971041,0.7306168069102793,0.7309023875185457,0.7313106012504538,0.7318340920473634,0.732465373327446,0.7331970014774369,0.7340217113876442,0.7349325163972008,0.735922776004162,0.7369862351764023,0.7381170392946064,0.7393097288012118,0.7405592175908389,0.7418607590894344,0.7432099038357081,0.7446024521890845,0.7460344055269146,0.7475019189455415,0.7490012580387515,0.7505287617998284,0.7520808131011358,0.7536538175821381,0.7552441911655114,0.7568483558652506,0.7584627430883367,0.7600838032886503,0.7617080206195985,0.7633319311466593,0.7649521432068045],[0.7517068599663337,0.7495885447199085,0.747491562326079,0.7454261935464632,0.7434033468653115,0.7414344866001118,0.7395315336205396,0.7377067338197311,0.7359724891237196,0.7343411457878442,0.7328247354148032,0.7314346663197101,0.7301813679668867,0.7290739013124299,0.7281195648602021,0.7273235481923356,0.7266887006006664,0.726215473397984,0.7259020527307762,0.7257446468399533,0.725737861213752,0.7258750973462416,0.726148930941245,0.7265514462246501,0.7270745173970111,0.7277100362914873,0.7284500891907036,0.72928708737773,0.7302138565051088,0.7312236898837883,0.732310370636023,0.7334681674746762,0.7346918087309897,0.7359764391697865,0.737317564089945,0.7387109851719915,0.7401527324528983,0.741638996624534,0.7431660655165551,0.7447302681053249,0.7463279286859508,0.7479553329886147,0.7496087070800916,0.7512842089552667,0.7529779318839265,0.754685917912072,0.7564041794720038,0.7581287268435511,0.7598555992098771,0.7615808972223315],[0.7495563141810011,0.7473288699752499,0.7451200869541632,0.7429405890942544,0.740801704882911,0.7387154052177227,0.7366942144222999,0.7347510890882276,0.7328992586570869,0.7311520207993347,0.7295224837998416,0.7280232475536397,0.7266660151460729,0.7254611307120157,0.7244170535895869,0.723539820629852,0.7228326292138485,0.7222957233063412,0.7219266484102115,0.7217207439684687,0.7216716951828559,0.7217720438276733,0.7220136255370321,0.7223879301396924,0.7228863906219726,0.723500608314998,0.7242225218039007,0.7250445263951817,0.7259595502472732,0.7269610926351477,0.7280432293444923,0.7292005898980767,0.7304283112101804,0.7317219723295187,0.7330775151293466,0.7344911560692037,0.7359592943899462,0.7374784221928412,0.7390450416707951,0.7406555942075159,0.742306405101758,0.7439936463586914,0.7457133184579299,0.7474612504581741,0.7492331164423955,0.7510244653109548,0.7528307603768378,0.7546474251010298,0.7564698915496109,0.7582936486426467],[0.747974219912496,0.7456655163500318,0.7433730650724641,0.7411076379684215,0.7388807506077413,0.7367046055733699,0.7345920095373416,0.7325562588272618,0.7306109873978236,0.7287699701728293,0.7270468736416942,0.725454944363507,0.7240066246332937,0.7227130829853602,0.7215836455099796,0.7206251145690216,0.7198410382504384,0.719231441311991,0.7187933705721405,0.7185216474190668,0.7184095190833458,0.7184491989329274,0.7186323095807811,0.7189502413056692,0.7193944365616058,0.7199566098010327,0.7206289104807262,0.7214040359558438,0.7222752999987357,0.7232366619153794,0.7242827206918409,0.7254086783107898,0.7266102763599083,0.7278837103273943,0.7292255265359889,0.7306325074478213,0.7321015519452199,0.733629557937153,0.7352133149671535,0.7368494141124239,0.7385341811767622,0.7402636370217268,0.7420334861481641,0.7438391318323618,0.7456757137704504,0.7475381626732072,0.749421265705318,0.7513197369571906,0.753228288005559,0.7551416947637029],[0.7469957312615803,0.7446366951195749,0.7422920340495838,0.7399724915571565,0.7376895554273006,0.735455400786928,0.7332828068537118,0.7311850421143571,0.7291757118442225,0.7272685609331542,0.7254772239063171,0.7238149128150924,0.7222940323392208,0.7209257101642216,0.7197192308903195,0.7186813765114043,0.7178157921549626,0.7171227815504044,0.7165997469854284,0.7162418826219774,0.7160428197935041,0.7159951706680261,0.7160909760965715,0.7163220689513383,0.7166803634159817,0.71715807924842,0.7177479086441045,0.718443132079049,0.71923768842822,0.720126203753527,0.7211039824661523,0.7221669641387749,0.7233116491452837,0.7245349966294133,0.7258342991432319,0.7272070397066892,0.7286507389594797,0.7301628022234046,0.7317403780803149,0.7333802406556219,0.7350787063712341,0.7368315922053015,0.7386342170861262,0.7404814423724627,0.7423677429943558,0.7442872986890158,0.7462340948673111,0.7482020243037997,0.7501849831832239,0.7521769573708972],[0.7466203397397345,0.7442416681991937,0.7418760145764876,0.7395339190591206,0.7372266285877334,0.7349660341015262,0.7327645808253722,0.7306351463761962,0.7285908807444621,0.7266450015025787,0.724810537073267,0.7231000110047973,0.7215250621318439,0.7200960022707911,0.7188213313600811,0.7177072688577827,0.7167574137796788,0.7159726604809968,0.7153514119702302,0.7148900052241217,0.7145832163695426,0.7144247519680756,0.7144076839085142,0.7145248157677198,0.7147689813309264,0.715133280261987,0.7156112567964344,0.7161970269551378,0.7168853589802568,0.717671710806031,0.7185522275413166,0.7195237012543076,0.7205834949181383,0.7217294323549104,0.7229596566435952,0.7242724610666542,0.7256660996244535,0.7271385885985695,0.7286875160271534,0.7303098803769766,0.7320019800336999,0.7337593688967021,0.7355768811235786,0.7374487147819163,0.7393685555068975,0.7413297195518489,0.7433252991436452,0.7453482985848665,0.7473917546813852,0.7494488388486188],[0.7468126714486056,0.7444416533024928,0.7420825457501081,0.73974550029158,0.7374413031707475,0.7351813035041613,0.7329773144017402,0.7308414825955586,0.7287861219752586,0.7268235067686334,0.724965621348992,0.7232238665578342,0.7216087281505056,0.7201294228005082,0.7187935513554623,0.7176068046213292,0.7165727751444693,0.7156929181335198,0.7149666734453085,0.7143917226317049,0.7139643307575013,0.7136797202203607,0.7135324360049947,0.7135166775004924,0.713626584616282,0.7138564739580942,0.71420102516692,0.7146554194899356,0.7152154332489389,0.7158774887303316,0.716638664505189,0.7174966665079388,0.7184497604967012,0.7194966659245615,0.7206364109854689,0.7218681490914478,0.7231909391653553,0.72460349748733,0.7261039394508986,0.727689545417229,0.729356597986257,0.7311003316944996,0.7329150030863465,0.7347940504431836,0.7367302963703903,0.7387161549107301,0.7407438213596533,0.7428054358473062,0.7448932189604307,0.7469995809887116],[0.7475086852942592,0.7451669430196806,0.7428358844870916,0.7405250963860339,0.7382447067783267,0.7360053057962123,0.733817841419814,0.7316934875149543,0.7296434819655466,0.7276789340457424,0.7258106024466237,0.724048648910007,0.7224023773884911,0.7208799747547893,0.7194882751875131,0.7182325742864999,0.7171165180182123,0.7161420840449892,0.7153096598540171,0.7146182073604508,0.71406549223842,0.7136483511381083,0.7133629710243485,0.7132051598185378,0.713170593706691,0.7132550320868261,0.7134544953852742,0.7137654037913111,0.7141846765821793,0.714709792450197,0.7153388113757063,0.7160703583195157,0.7169035684768745,0.7178379931355117,0.7188734643829036,0.7200099161002799,0.721247158091784,0.722584600700584,0.7240209325433127,0.725553777369868,0.7271794187601127,0.7288927314902306,0.730687352263666,0.7325559683602529,0.7344906104772896,0.7364829082667943,0.738524302677656,0.7406062186588167,0.7427202034421034,0.7448580354736687],[0.7486252557996147,0.7463277306089853,0.7440392334487727,0.7417686525495205,0.739525321537402,0.7373189383258266,0.7351594631940086,0.7330569950196087,0.7310216256468511,0.7290632738837797,0.7271915027008187,0.7254153258236159,0.723743012880482,0.7221819051351508,0.7207382559027572,0.7194171101626731,0.718222235951725,0.7171561156929842,0.7162199993375231,0.715414014413275,0.714737322329758,0.7141883067059971,0.7137647784118154,0.7134641830422105,0.7132837988836868,0.713220916257011,0.7132729918159961,0.7134377735983802,0.7137133942368217,0.7140984307598813,0.7145919299261917,0.7151933981397531,0.7159027547827235,0.7167202473483434,0.7176463261148508,0.7186814753075799,0.7198259967724101,0.7210797411394538,0.7224417802927116,0.7239100137273641,0.7254807382700285,0.727148532547083,0.7289066035312988,0.7307471709412408,0.7326617872740018,0.7346416015006918,0.7366775746534461,0.7387606544448824,0.740881915104877,0.7430326677807746],[0.7500706052314632,0.7478256201632305,0.7455873981971812,0.7433640571836306,0.7411640773395527,0.7389962245134446,0.7368694574558137,0.734792819306773,0.7327753144786637,0.7308257733437789,0.7289527085977877,0.7271641687534522,0.725467595737228,0.7238696947411745,0.7223763250046203,0.7209924197726812,0.7197219421421587,0.7185678809254086,0.7175322873646202,0.7166163500360552,0.7158205021734338,0.7151445533745762,0.714587836465479,0.7141493601538226,0.7138279587863889,0.7136224317165725,0.7135316661775536,0.7135547388969072,0.7136909928186945,0.7139400861378487,0.7143020113761707,0.7147770824533282,0.7153658876621202,0.7160692061842551,0.7168878853245076,0.7178226750588653,0.7188740159386849,0.7200417764723411,0.7213249397721839,0.7227212600712614,0.7242269794405968,0.7258367671962878,0.7275439222606728,0.7293406919053469,0.7312185838730267,0.7331686353071081,0.7351816361774698,0.7372483120299916,0.739359471671267,0.7415061249732826],[0.7517536646052168,0.7495636863972572,0.7473775334997825,0.7452025412987742,0.7430463456775569,0.7409168151452203,0.7388219713672922,0.7367698989214728,0.7347686458479898,0.7328261174172697,0.7309499664421384,0.7291474843299143,0.7274254977831653,0.7257902764794464,0.724247457057563,0.7228019882153365,0.7214581006564873,0.7202193040801752,0.7190884115472521,0.718067589609653,0.71715843079808,0.7163620436352685,0.7156791544051346,0.715110214492678,0.7146555071591668,0.7143152480163847,0.7140896740725542,0.7139791169062789,0.7139840561737503,0.7141051501926661,0.7143432407332069,0.7146993293753982,0.7151745228933918,0.7157699451836481,0.7164866134501978,0.7173252771014095,0.7182862199784548,0.7193690318733377,0.7205723664354664,0.7218937205415055,0.7233292870295366,0.7248739277608726,0.7265212761092844,0.7282639329971853,0.730093703803803,0.7320018353736137,0.733979231583167,0.7360166395952876,0.7381048059619774,0.740234604705321],[0.7535914354864253,0.7514541816881776,0.7493171500711819,0.7471869261091234,0.7450703568789949,0.7429744944103815,0.7409065309045615,0.7388737268076153,0.736883333237745,0.7349425108081392,0.733058247409625,0.7312372779658103,0.7294860094828601,0.7278104548218199,0.7262161784702268,0.7247082571524692,0.7232912574006177,0.7219692312548763,0.720745730157733,0.719623835955366,0.7186062068371426,0.7176951351284324,0.7168926131723987,0.7162004031225606,0.7156201063106099,0.7151532279130458,0.7148012328571626,0.7145655892185216,0.7144477957125723,0.7144493902346623,0.7145719367440397,0.7148169881442454,0.7151860232616726,0.7156803567176061,0.7163010216826218,0.7170486275767927,0.7179231981948646,0.7189240007935026,0.7200493829393197,0.7212966394039195,0.7226619324802698,0.7241402824975907,0.7257256316763621,0.7274109695467171,0.7291884987431457,0.7310498186444802,0.7329861087364368,0.7349882998652204,0.737047227094847,0.7391537617769302],[0.7555142097804044,0.7534238687920276,0.7513295169961522,0.7492370481104621,0.7471525995656207,0.7450825077968906,0.7430332578948619,0.74101142851141,0.739023633249452,0.7370764600894122,0.7351764106931107,0.7333298416445684,0.731542909803643,0.7298215239327298,0.728171304588109,0.7265975539386906,0.7251052366958521,0.7236989727367603,0.7223830413236132,0.7211613961163909,0.7200376895032394,0.7190153041812277,0.7180973894491387,0.7172868993448426,0.7165866295770551,0.7159992501547723,0.715527330687838,0.7151733554969393,0.7149397259136911,0.7148287474667183,0.7148426000528529,0.7149832897253199,0.715252581465939,0.7156519133490858,0.7161822939699239,0.7168441869893439,0.717637389121711,0.7185609105992381,0.7196128694771431,0.7207904121593216,0.722089671274218,0.723505768130534,0.7250328611087066,0.7266642351377114,0.7283924226823452,0.7302093444850369,0.7321064586143109,0.7340749083380265,0.7361056619622215,0.7381896403084234],[0.75746892099905,0.7554173697378341,0.7533569812376082,0.7512930240240252,0.7492310098750778,0.7471766608316394,0.7451358722392035,0.7431146725161654,0.74111918054573,0.7391555617725846,0.7372299842347875,0.7353485758581464,0.7335173843680143,0.7317423411186508,0.730029229995441,0.7283836623102236,0.7268110582932558,0.725316635403948,0.7239054032605459,0.7225821645550872,0.7213515209040746,0.7202178822149996,0.7191854778465383,0.7182583676213483,0.7174404506229797,0.7167354696742617,0.7161470094516911,0.7156784863363643,0.7153331283376744,0.7151139437588925,0.7150236777204779,0.7150647562434882,0.7152392183532227,0.7155486376193738,0.7159940357079516,0.7165757918372635,0.7172935533807326,0.7181461540193474,0.7191315465065728,0.72024675694322,0.7214878662527816,0.7228500223267719,0.724327483410333,0.7259136902915782,0.7276013623538801,0.729382610979875,0.7312490632897692,0.7331919896049854,0.7352024290424396,0.7372713089330125],[0.7594210280946845,0.7573990108365758,0.7553627638079987,0.7533169920420201,0.7512666568906263,0.7492169541505926,0.7471732892941103,0.7451412502620245,0.7431265783898273,0.7411351381315858,0.7391728863151841,0.7372458416945555,0.7353600555530589,0.7335215840515075,0.7317364629025616,0.7300106847924324,0.728350179767679,0.72676079857008,0.7252482986502689,0.7238183323373502,0.7224764364039519,0.7212280220601017,0.7200783642487208,0.7190325890110922,0.7180956576499598,0.7172723464456701,0.7165672207800762,0.7159846026963219,0.7155285311735591,0.7152027147289485,0.7150104763809969,0.7149546915233764,0.7150377198666178,0.7152613332941948,0.7156266422168539,0.7161340237333729,0.7167830555237655,0.7175724597920548,0.7185000616126926,0.7195627656163448,0.7207565540420527,0.7220765078452811,0.723516850947417,0.7250710160735042,0.7267317291935966,0.7284911085484662,0.7303407736965601,0.7322719599570168,0.7342756339547651,0.7363426065694386],[0.7613552993573088,0.7593535729232832,0.7573316794519315,0.7552938080866469,0.7532444271897942,0.7511882729709662,0.7491303359050786,0.7470758451608153,0.7450302513103633,0.7429992076282554,0.7409885503057934,0.739004277903876,0.7370525303381545,0.7351395676350103,0.7332717486156519,0.7314555095617049,0.7296973427944126,0.7280037749683732,0.726381344748715,0.7248365794176386,0.7233759698525475,0.7220059432429421,0.7207328328751887,0.7195628443196622,0.7185020174082984,0.7175561834951572,0.716730917649567,0.7160314856409977,0.7154627858361469,0.7150292864397431,0.7147349588671636,0.7145832084314321,0.7145768039460458,0.7147178082666634,0.7150075121867008,0.7154463744211987,0.7160339706080171,0.7167689542713604,0.7176490324838636,0.718670958505215,0.7198305429759274,0.7211226843522858,0.7225414182671299,0.72407998449854,0.7257309093348475,0.7274861004307147,0.7293369508110835,0.7312744485119007,0.7332892884256006,0.7353719831961862],[0.7632757633819205,0.7612862289302748,0.7592700727381767,0.7572309957643834,0.7551730075155945,0.7531004247544766,0.751017868476058,0.7489302591520908,0.7468428102477036,0.7447610200099605,0.7426906615121553,0.7406377709099592,0.7386086338259187,0.7366097697284899,0.7346479141132644,0.7327299982311284,0.7308631260457801,0.7290545480473428,0.7273116315063006,0.7256418267294421,0.7240526288832559,0.7225515349858184,0.7211459957398352,0.7198433619896973,0.7186508257348807,0.7175753558195522,0.7166236286406872,0.7158019544693688,0.7151162002554601,0.7145717100757252,0.7141732246789193,0.7139248018648487,0.7138297396915927,0.71389050471633,0.714108667618062,0.7144848486008457,0.7150186749105222,0.715708752597394,0.7165526543117824,0.7175469244321454,0.7186871022161909,0.7199677629707995,0.7213825765072146,0.722924381442182,0.7245852732812,0.7263567037252023,0.7282295883093426,0.73019441932531,0.732241380991052,0.7343604639927903],[0.7652049795279001,0.7632218195174099,0.7612051162986448,0.759158087437542,0.7570842915340767,0.7549876368435512,0.7528723885917981,0.7507431747869953,0.7486049902977724,0.7464631989276853,0.7443235331704976,0.7421920912803088,0.7400753312375613,0.7379800611394304,0.7359134254951245,0.7338828868680425,0.7318962022831508,0.729961393815294,0.728086712798387,0.7262805971520885,0.7245516214162021,0.7229084392168827,0.7213597180640064,0.7199140665948763,0.7185799546322724,0.717365626708586,0.7162790100136729,0.7153276180408267,0.7145184515195346,0.7138578985201917,0.7133516358782782,0.7130045342965086,0.7128205696260902,0.7128027428864612,0.7129530115427064,0.7132722344107698,0.7137601322970271,0.7144152661017504,0.7152350336344571,0.7162156858208399,0.7173523623523599,0.7186391461744683,0.720069135566291,0.7216345319730519,0.7233267412489589,0.7251364855820149,0.7270539231224507,0.7290687722306295,0.7311704372942444,0.7333481332240952],[0.7671826764332843,0.7652035030930325,0.7631834930538983,0.761125361772431,0.7590321979995924,0.7569074823650737,0.7547551051575438,0.7525793829370463,0.7503850735473262,0.7481773890216811,0.7459620057979892,0.7437450715797658,0.7415332081042583,0.7393335090106036,0.7371535319466597,0.735001284018858,0.732885199682425,0.7308141101968324,0.7287972038403667,0.7268439761944646,0.7249641699776,0.7231677041327049,0.7214645921511617,0.7198648499469312,0.7183783939690861,0.7170149306488119,0.7157838387025941,0.714694046238135,0.7137539050118211,0.7129710645427384,0.712352349074133,0.7119036405658039,0.7116297709798483,0.7115344270718283,0.7116200707104051,0.7118878774190287,0.7123376953703939,0.7129680264838638,0.7137760306024636,0.7147575529911728,0.7159071746393529,0.717218284107274,0.7186831689695237,0.7202931243127497,0.7220385752713191,0.7239092102528869,0.7258941213271052,0.7279819482246691,0.7301610225108148,0.7324195087390625],[0.7692637245376436,0.7672907266664842,0.765269387622809,0.763201880368893,0.7610907794776937,0.758939089817195,0.7567502751164785,0.7545282859231277,0.7522775863570635,0.7500031789537529,0.7477106267727611,0.7454060718298653,0.7430962487976509,0.7407884928172211,0.738490740180098,0.7362115205835282,0.7339599396438807,0.7317456503818295,0.7295788124795248,0.7274700382630978,0.725430324590972,0.7234709701341953,0.7216034779201962,0.7198394434720518,0.7181904294019478,0.7166678278941497,0.7152827131172741,0.7140456862095889,0.7129667160512441,0.7120549795370115,0.711318705454856,0.7107650263239229,0.7103998426201419,0.7102277036969944,0.710251709382927,0.7104734357087625,0.7108928875061555,0.7115084797536224,0.7123170485740323,0.7133138917597954,0.7144928376770809,0.7158463404359492,0.7173655983619639,0.7190406921102654,0.7208607382563426,0.7228140538956925,0.7248883276894784,0.7270707928937786,0.7293483981833834,0.7317079724961711],[0.7715153524830306,0.7695564020874534,0.7675416443192519,0.7654726522397456,0.763351420723086,0.7611804052569546,0.7589625615753953,0.7567013855612352,0.7544009527141354,0.7520659563260148,0.7497017433414447,0.7473143467110946,0.7449105128775609,0.7424977228728754,0.7400842053654975,0.7376789398833659,0.7352916483719563,0.7329327732369577,0.7306134400854091,0.7283454035320165,0.7261409746924467,0.7240129293533596,0.7219743962957721,0.7200387258535061,0.7182193395032908,0.7165295620888572,0.714982439148848,0.7135905427072612,0.712365769745358,0.7113191383478965,0.710460587142826,0.7097987840722193,0.7093409506905474,0.7090927080453072,0.7090579497346783,0.7092387469611434,0.7096352893382631,0.7102458639144388,0.7110668734279496,0.7120928932919566,0.7133167653228165,0.7147297248633162,0.7163215567957214,0.7180807750503266,0.7199948196321042,0.722050264924176,0.7242330330709507,0.7265286065636182,0.7289222346987483,0.7313991292996824],[0.7740134926568263,0.7720831428264381,0.7700899142017588,0.7680347135683143,0.7659188770690442,0.7637442187436242,0.7615130811568085,0.7592283875549642,0.7568936948137892,0.7545132462424344,0.7520920230921426,0.7496357933848928,0.7471511564354905,0.7446455811974738,0.7421274363304746,0.7396060096785906,0.7370915146834053,0.7345950811519896,0.7321287277825002,0.7297053139423783,0.7273384684212735,0.7250424932654423,0.722832241360588,0.7207229671764468,0.718730151018053,0.7168692982300514,0.7151557160384321,0.7136042720357348,0.7122291396484697,0.7110435371791739,0.7100594680880297,0.7092874709643324,0.7087363880374402,0.7084131610107866,0.708322662423305,0.7084675696443253,0.7088482870322033,0.7094629198227397,0.7103073010908221,0.71137507080591,0.7126578037482676,0.7141451810299126,0.7158251983084309,0.7176844025903729,0.7197081488446524,0.7218808674876122,0.7241863341198174,0.7266079336156986,0.7291289116949106,0.7317326083333098],[0.776838154665799,0.77495842692495,0.7730096198083531,0.770991910534398,0.7689058960039585,0.7667526499961378,0.7645337839990144,0.7622515112107856,0.7599087130442886,0.7575090072324314,0.7550568163635698,0.7525574353760167,0.7500170962138505,0.747443027499101,0.7448435067192231,0.7422279020789718,0.739606700842931,0.7369915207252873,0.7343951006987843,0.7318312675323321,0.7293148744675026,0.7268617087509497,0.7244883652936492,0.7222120845631301,0.7200505539532099,0.7180216733189368,0.7161432870870635,0.714432887295295,0.7129072939796683,0.7115823213833473,0.7104724403338201,0.7095904486402569,0.708947162308595,0.7085511405917421,0.7084084572690901,0.7085225290406449,0.7088940095749974,0.7095207547112015,0.7103978608114632,0.7115177745829107,0.7128704691446096,0.7144436780047874,0.716223176172584,0.7181930960157905,0.7203362647527369,0.7226345506013994,0.7250692054925396,0.7276211937228896,0.7302714977886074,0.7330013947063527],[0.7800677853777304,0.7782686121491351,0.7763956256589524,0.7744482296092119,0.7724262166004576,0.770329831905836,0.7681598426149295,0.7659176118875843,0.7636051778472868,0.7612253363875392,0.7587817268595053,0.7562789192525063,0.7537225010705143,0.7511191616504935,0.7484767711693475,0.7458044510582855,0.7431126320064858,0.7404130952188904,0.7377189921345586,0.7350448374621689,0.7324064702089081,0.7298209774388104,0.7273065758737447,0.724882447222308,0.7225685243580051,0.7203852272167188,0.7183531495571849,0.7164927004875431,0.7148237077989898,0.7133649934794322,0.7121339350422816,0.7111460291689634,0.7104144762635891,0.7099498055008973,0.7097595595304287,0.709848056027815,0.7102162397840386,0.7108616342229005,0.7117783955505524,0.7129574667187539,0.7143868226290053,0.7160517930811954,0.7179354463156485,0.7200190138664361,0.7222823368880563,0.7247043150029119,0.7272633407693136,0.7299377057353309,0.732705967350152,0.7355472694101116],[0.7837726879291717,0.7820918501154139,0.7803346290300396,0.7784996500409744,0.7765858733243233,0.774592660961951,0.7725198511317977,0.770367839441171,0.7681376672621365,0.765831116681925,0.7634508113714482,0.761000322293318,0.7584842767099311,0.7559084684070565,0.7532799664174222,0.7506072188160634,0.7479001473767894,0.7451702280502202,0.7424305513860255,0.739695856230854,0.7369825293656692,0.7343085633016343,0.7316934643552686,0.7291581035132189,0.7267245036264484,0.7244155582878263,0.722254680459258,0.7202653825729523,0.7184707943809651,0.7168931300705182,0.715553121732638,0.71446944162716,0.713658140146068,0.7131321291962347,0.7129007412218593,0.7129693917995256,0.7133393685530862,0.7140077613830618,0.7149675394581008,0.7162077701775893,0.7177139656223556,0.7194685340023455,0.7214513081164594,0.7236401202574556,0.7260113932674965,0.7285407201447414,0.7312034090463894,0.7339749759716545,0.7368315731289669,0.7397503464203685],[0.7880077426270202,0.7864901333330618,0.7848964890502776,0.7832247123209598,0.7814729638064697,0.779639728325821,0.7777238894032317,0.7757248127568727,0.773642439023616,0.7714773858195227,0.7692310589698841,0.766905772391219,0.7645048756549366,0.7620328876923695,0.7594956343985753,0.7569003870458105,0.7542559974210606,0.7515730244598302,0.7488638458806025,0.7461427469733846,0.7434259773345948,0.7407317650813697,0.7380802770805751,0.7354935132031767,0.7329951228264844,0.7306101330578771,0.7283645807579398,0.726285044673133,0.7243980800082789,0.7227295655256591,0.7213039823827266,0.7201436536467636,0.7192679825655396,0.7186927347127787,0.7184294124556108,0.718484768465263,0.7188604975520159,0.7195531333055903,0.7205541593301179,0.7218503266339458,0.7234241516961335,0.7252545563383876,0.7273176024124812,0.7295872719916038,0.7320362466930151,0.7346366466686324,0.7373606990524743,0.7401813156692304,0.7430725693152649,0.7460100660749613],[0.7928048920912666,0.7915009575264312,0.7901249913581903,0.7886743077296253,0.7871463843077035,0.7855389221454792,0.7838499148193727,0.7820777276590412,0.7802211878345604,0.7782796859635607,0.7762532897338572,0.7741428697856906,0.7719502377390981,0.7696782957594386,0.7673311963978005,0.7649145105907315,0.7624354006233418,0.7599027935228803,0.7573275487377575,0.7547226120693215,0.7521031456912528,0.7494866217921579,0.7468928650567478,0.7443440270971414,0.7418644744096146,0.7394805709448439,0.7372203375492596,0.735112974058054,0.7331882363858759,0.7314756710794219,0.7300037235418235,0.7287987528399332,0.7278840039616434,0.7272786047723423,0.7269966660444875,0.7270465650393876,0.7274304835624168,0.7281442499116119,0.7291775034601622,0.7305141661807065,0.732133173827823,0.7340093964938972,0.7361146671042437,0.7384188372961377,0.7408907906513005,0.7434993596843221,0.7462141114939607,0.7490059845001005,0.7518477732948575,0.7547144695006297],[0.7981660958539885,0.7971293661524433,0.796028876718947,0.7948615767700359,0.7936244756470223,0.7923146914265545,0.7909295086248411,0.7894664461061487,0.7879233363523127,0.7862984172666435,0.7845904376583065,0.7827987774626655,0.780923583574284,0.7789659218703349,0.7769279455432166,0.7748130791935147,0.7726262172003204,0.7703739336196022,0.7680646991920692,0.7657090989004705,0.7633200408461567,0.760912943991397,0.7585058885735674,0.7561197088787799,0.7537780038637628,0.7515070373628331,0.749335497142196,0.7472940820585373,0.7454148905935238,0.7437305938442484,0.7422733932804059,0.7410737890227238,0.7401592169881488,0.7395526489650034,0.7392712809994011,0.7393254522837436,0.7397179294154232,0.7404436549484941,0.741489999139038,0.7428374833958152,0.7444608812342928,0.7463305624365106,0.7484139348959409,0.7506768530598162,0.7530848927342728,0.7556044288039024,0.7582034868879576,0.7608523674043424,0.7635240594198198,0.7661944726213357],[0.8040576776983853,0.8033414121551645,0.8025742887972849,0.8017531992978844,0.8008749959233625,0.7999365249049226,0.7989346676474798,0.797866390993888,0.7967288078936637,0.7955192499535355,0.794235353463178,0.792875160579843,0.7914372374008093,0.7899208106251536,0.788325924368381,0.7866536183936614,0.784906128493799,0.783087108910618,0.7812018754021737,0.779257665727829,0.7772639117593956,0.7752325139724527,0.7731781045614777,0.7711182797368974,0.7690737748959012,0.7670685485287339,0.7651297325333315,0.7632873992881707,0.7615740915043505,0.7600240628442592,0.758672190095713,0.7575525465766154,0.7566966756257278,0.7561316721118143,0.7558782588242013,0.7559491100745166,0.7563476938942838,0.7570678498753419,0.7580941928937057,0.7594032722155143,0.7609652794240025,0.7627460315198454,0.7647089650403908,0.7668169392924784,0.769033727962487,0.771325152385564,0.773659864087677,0.7760098170716044,0.7783504855173524,0.7806608855402156],[0.810407111757123,0.8100602421476428,0.8096800253313086,0.8092636606662457,0.8088082261652225,0.8083106947227636,0.8077679559908266,0.8071768449930243,0.8065341787408211,0.805836802309128,0.805081646041978,0.8042657957876215,0.8033865782987142,0.8024416641635073,0.8014291908356059,0.800347908467873,0.7991973512774376,0.797978036996286,0.7966916964850216,0.7953415346525907,0.7939325222238541,0.7924717153561194,0.7909685962785713,0.7894354225986724,0.7878875652261113,0.7863438045701572,0.7848265415010162,0.7833618637066084,0.781979390639651,0.7807118041174301,0.7795939627147654,0.7786615069250971,0.7779489049723542,0.7774869860095023,0.7773001698864931,0.7774038067561958,0.7778021951856969,0.778487815700825,0.7794420260512235,0.7806370319738738,0.7820386170969471,0.7836090405399705,0.7853096474308616,0.7871029473752136,0.7889540942852147,0.7908318127049667,0.7927088683379022,0.7945621938885183,0.7963727734198651,0.7981253712821715],[0.817103239212519,0.8171659809060793,0.8172169878463683,0.8172541416541543,0.8172751490360415,0.8172775415206959,0.8172586781358842,0.8172157517807996,0.817145800206292,0.8170457227058172,0.8169123038474987,0.8167422458481236,0.816532211507985,0.8162788799942945,0.8159790181800427,0.8156295707076155,0.8152277724345267,0.8147712873968337,0.8142583788315847,0.8136881150292437,0.8130606156760467,0.8123773426438163,0.8116414375197298,0.8108581050090815,0.8100350359541133,0.8091828551150471,0.8083155658342778,0.8074509448587932,0.80661081461032,0.8058210864104088,0.8051114278803245,0.8045143669319845,0.8040636200679653,0.8037914637177597,0.8037251360007583,0.8038826815283635,0.8042693296330526,0.8048759241850149,0.805680267932525,0.8066507414832255,0.8077506741049916,0.8089422328344157,0.8101892993571054,0.8114592984929113,0.8127241574040136,0.8139606264299203,0.8151501732466663,0.816278619371962,0.817335642996071,0.8183142330551172],[0.8240006087702131,0.8245002806159222,0.8250129027210394,0.8255373575891497,0.8260723310479419,0.8266162982677197,0.8271675100373944,0.8277239796115594,0.8282834705373314,0.828843485992554,0.8294012603256632,0.8299537536920071,0.8304976509438489,0.8310293662662375,0.8315450554750599,0.8320406384251651,0.8325118346334106,0.8329542160186649,0.8333632816034903,0.8337345600969973,0.8340637474361571,0.8343468874935706,0.8345806050522815,0.8347624004305323,0.8348910141918638,0.8349668672108941,0.8349925744712692,0.8349735181371734,0.8349184435973855,0.8348400074048654,0.8347551539138552,0.834685124218976,0.8346548062401268,0.8346910264629638,0.8348192939975577,0.8350585878951621,0.8354148406696847,0.8358771339764588,0.8364208177127979,0.8370143550067056,0.8376251895007905,0.8382234942789535,0.8387841433476004,0.8392874336995351,0.8397190163491629,0.8400693831980738,0.8403331499200134,0.8405082880691386,0.8405953953398483,0.8405970489230582],[0.8309280731325142,0.8318757661406322,0.832862675497442,0.8338888789898399,0.8349542609814453,0.8360584882144986,0.837200983641078,0.8383808981793457,0.8395970803043059,0.8408480434087491,0.84213193091456,0.8434464791858911,0.8447889784053702,0.8461562317382864,0.8475445133486673,0.8489495261730572,0.8503663608383212,0.8517894577739471,0.8532125754712724,0.854628769044465,0.8560303848166195,0.8574090786471282,0.8587558681615037,0.8600612318988307,0.8613152714667778,0.8625079556301546,0.8636294669143856,0.8646706700123469,0.8656237139172798,0.8664827610225255,0.8672447981524283,0.8679104146825072,0.868484316993933,0.8689751747569648,0.8693941677859941,0.8697513690009865,0.8700492936406644,0.870277796365847,0.8704185164328985,0.8704523388896299,0.8703638925053848,0.8701434184678652,0.8697869750604125,0.869295748169173,0.8686749926354621,0.8679329186833074,0.8670796862113317,0.8661265736446812,0.8650853331808909,0.8639677165126741],[0.8377010165014922,0.8390897216570392,0.8405437053169651,0.8420642591432365,0.8436524931585245,0.8453093037293891,0.8470353379168495,0.8488309537827237,0.850696176186406,0.8526306475478975,0.8546335729903675,0.8567036592122391,0.8588390463798047,0.8610372322850794,0.8632949879930969,0.8656082642281441,0.867972087849054,0.8703804479826933,0.8728261717828688,0.8753007904437359,0.8777943971365219,0.8802955001063478,0.882790876451882,0.8852654353415114,0.8877021038435345,0.8900817543890752,0.8923832002486171,0.8945832940686853,0.8966571735512208,0.8985787053475267,0.9003211778242743,0.901858274690688,0.9031653049267646,0.9042205433378813,0.9050063503816037,0.9055096451468879,0.9057217381088615,0.9056384686718082,0.905261361374663,0.9045988169810679,0.9036660863410014,0.9024840146183433,0.901077227161398,0.8994723301954335,0.8976964138600698,0.8957759399737341,0.8937359920541448,0.8915998239081441,0.8893886347478599,0.8871215052395248],[0.8441357961257306,0.8459404130457681,0.8478343441806376,0.8498199219425555,0.8518992960038422,0.8540743934078725,0.8563468737233424,0.8587180786439629,0.8611889753460984,0.8637600928110404,0.8664314501939345,0.8692024761753202,0.8720719180616581,0.8750377392069488,0.8780970031094153,0.8812457422996078,0.8844788098896776,0.8877897114182078,0.8911704144366925,0.8946111332023646,0.8981000859632833,0.901623222794895,0.9051639229988989,0.9087026630416285,0.9122166593794881,0.9156794959919345,0.9190607550034386,0.9223256818064571,0.9254349355584256,0.9283445046930298,0.9310059095880325,0.9333668777426146,0.9353727704817351,0.9369691688925293,0.938106141625995,0.9387445386477629,0.9388634074991353,0.938465075963926,0.937574148363217,0.9362313796077862,0.9344865608576304,0.9323928844781026,0.9300031502027686,0.9273674435349147,0.9245318586753193,0.9215379267443083,0.9184225008506475,0.9152179209009538,0.9119523349100072,0.9086500938242832],[0.8500643809760314,0.8522437011584526,0.8545327735361063,0.8569346363168473,0.859452112354398,0.8620877588571684,0.8648438107975375,0.8677221173151011,0.8707240703148358,0.8738505243518695,0.8771017067650767,0.8804771168676878,0.8839754128198077,0.8875942845898106,0.8913303111536917,0.8951787997791789,0.8991336048925361,0.903186923633979,0.9073290647861612,0.9115481873423618,0.9158300046335291,0.9201574497806179,0.9245102985014493,0.92886474635771,0.9331929400096317,0.9374624669828155,0.9416358174851773,0.9456698474898686,0.9495152984536435,0.9531164711786285,0.9564112168436573,0.9593315059146209,0.961804973415438,0.9637580183693056,0.9651212411636404,0.9658381924186275,0.9658783737886362,0.9652500566178355,0.963996144983835,0.9621795437903055,0.9598717676299189,0.9571455345446475,0.9540703297844713,0.9507100449512238,0.9471219818460604,0.9433566958143443,0.9394583133724286,0.935465084153201,0.9314100185851624,0.927321525613482],[0.8553469810426312,0.8578473485602848,0.8604732354480775,0.8632279597214771,0.8661145516301333,0.869135689446512,0.8722936274221905,0.8755901151402233,0.8790263074241179,0.8826026638902155,0.886318837150212,0.8901735485837119,0.8941644505072,0.8982879734658095,0.9025391572696476,0.9069114642903274,0.9113965734329632,0.9159841531170446,0.9206616115596391,0.9254138226976091,0.9302228262827542,0.9350675011570664,0.9399232116701565,0.9447614289825681,0.9495493321795091,0.9542493996355316,0.9588190104268107,0.9632100911420601,0.9673688687579399,0.9712358304119009,0.9747460525786221,0.9778301526968352,0.9804162407908773,0.9824334017704771,0.9838173783387045,0.9845190362032592,0.9845148706635349,0.98381442719005,0.9824576126084411,0.9805042966087261,0.9780238573887651,0.9750877636513128,0.9717650693180111,0.9681200269703294,0.9642110753169028,0.9600906395418245,0.9558053657775678,0.9513965550803369,0.9469006628889607,0.9423497941167703],[0.8598807970641205,0.8626408093918471,0.8655369993992545,0.8685725396728675,0.8717502087378328,0.8750723107333189,0.8785405857412765,0.8821561099967112,0.8859191851906061,0.8898292160737943,0.8938845755874691,0.8980824567913671,0.902418710944955,0.9068876712342497,0.9114819618467477,0.9161922924051124,0.9210072382117722,0.9259130073783323,0.9308931967785103,0.9359285399554569,0.9409966517453515,0.9460717765963076,0.9511245505563422,0.9561217909209058,0.9610263328753492,0.9657969395113047,0.9703883207724352,0.974751308679557,0.9788332511079278,0.9825787048968112,0.9859305312479038,0.988831520614119,0.9912266925715449,0.993066400167799,0.9943102407793912,0.9949313965600666,0.9949203416928198,0.9942863258781025,0.9930556481061042,0.9912674444475857,0.988968835389823,0.9862108744914726,0.9830457352151033,0.9795249420145572,0.9756983001228203,0.9716132489595132,0.9673144696037221,0.9628436529592429,0.9582393781541745,0.953537071965673],[0.8636038273921565,0.8665592580684028,0.8696566039575969,0.8728985526209049,0.8762872756429166,0.8798243332383375,0.8835105685277087,0.8873459908397203,0.8913296474587836,0.8954594833370959,0.8997321884434839,0.9041430326437728,0.9086856883213926,0.9133520413805102,0.9181319918640481,0.9230132462120008,0.9279811042411207,0.9330182453200251,0.9381045200361887,0.9432167560146802,0.9483285895811427,0.9534103388029034,0.9584289382225943,0.9633479614013036,0.9681277641692045,0.9727257889251558,0.9770970775846335,0.9811950460191831,0.9849725725205444,0.988383440612191,0.9913841419235041,0.9939359724940503,0.9960072287452311,0.9975751239662961,0.9986268538256213,0.9991592120886822,0.9991765829748152,0.9986880949161955,0.9977055095325729,0.9962429337632106,0.994317944455317,0.9919528495021085,0.9891751848710107,0.9860173067668507,0.982515368762118,0.978708039893048,0.9746352246714627,0.9703369305019165,0.9658523422198445,0.961219111926008],[0.8664937202751449,0.8695818800491877,0.8728134435521746,0.8761904126809928,0.8797141596747388,0.8833853214045222,0.8872036833866013,0.8911680531820927,0.8952761230067181,0.8995243215976411,0.9039076556892268,0.9084195418574069,0.9130516300308671,0.9177936206699375,0.9226330785217357,0.9275552470217873,0.932542868885009,0.9375760202775667,0.9426319682554013,0.9476850639635986,0.9527066874686827,0.9576652640631893,0.9625263763859546,0.967253001553505,0.9718059072731595,0.9761442447872463,0.9802263780297451,0.9840109851362668,0.9874584565688941,0.9905325877087305,0.9932025142755021,0.9954447545433729,0.9972450875325173,0.9985997921862766,0.9995154835782707,1.0000064575036574,1.0000885495347476,0.9997707394085233,0.9990507103653984,0.9979192718927747,0.9963686449006398,0.9943982000007817,0.9920165561036636,0.9892413108895419,0.9860976245417402,0.9826164051034798,0.9788324915582121,0.9747830226421602,0.9705060645543847,0.9660395098727573],[0.868562639374112,0.8717256224752139,0.8750301821362588,0.8784775828856587,0.8820683750890357,0.8858022861686841,0.8896781028157261,0.8936935443087347,0.89784512731153,0.9021280228599109,0.9065359066802,0.9110608045320434,0.9156929349580158,0.9204205526795433,0.925229796931462,0.9301045503052826,0.9350263152006761,0.9399741167852853,0.9449244434378516,0.9498512379740622,0.9547259554549498,0.9595177059045323,0.9641935025500965,0.9687186378069176,0.9730572094802962,0.9771728175492501,0.9810294460227273,0.9845925328620474,0.9878302115679206,0.9907146782613611,0.9932235957684614,0.9953413903088559,0.9970602278916066,0.99838037907399,0.9993095890372973,0.9998609149855044,1.000047995422605,0.9998754599499249,0.9993312964263898,0.9983975534973626,0.9970610496390798,0.9953170163240728,0.9931697535492692,0.9906320467843519,0.9877239949700465,0.9844715811584391,0.9809051897144592,0.9770581971854259,0.9729657099054496,0.9686634832105547],[0.8698497356068255,0.8730363338288787,0.8763603316854351,0.879822324741719,0.883422150652264,0.8871587848239069,0.8910302292659688,0.8950333952207258,0.8991639804926567,0.9034163427978461,0.9077833709479738,0.9122563562794004,0.916824867449318,0.9214766325582623,0.9261974335273117,0.9309710187574726,0.9357790413131367,0.940601031166485,0.9454144113501161,0.9501945690824497,0.9549149938847685,0.9595474951474197,0.9640625111651261,0.9684295198526276,0.9726175575209784,0.9765958454270423,0.9803345133486924,0.9838053941684972,0.9869828424555569,0.989844502801595,0.992371920539315,0.9945508503962797,0.996371082576478,0.9978255826896106,0.9989087668328548,0.9996139365538249,0.999930800881024,0.9998468928612104,0.9993553048201373,0.9984553901057921,0.9971497771674138,0.9954445855649927,0.9933502460119348,0.9908818929316987,0.9880592519428909,0.984906148554632,0.9814497842839689,0.9777199031081737,0.9737479398415184,0.9695662128209949]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x2","y":[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],"yaxis":"y2","z":[[0.1345851521283475,0.13397995776700128,0.13339061038909922,0.1328225911550461,0.13228149756300472,0.13177294130326805,0.13130243433789268,0.13087526608472483,0.1304963754965416,0.13017022264085434,0.12990066501380884,0.12969084417396357,0.1295430882838845,0.12945883575177458,0.12943858436209818,0.12948186910837653,0.1295872704728327,0.12975245325373527,0.12997423436319416,0.13024867645229515,0.13057120289946886,0.1309367287239777,0.13133980141977528,0.13177474556042723,0.13223580527532955,0.1327172792793078,0.13321364396825627,0.13371966108032415,0.13423046747541756,0.1347416456268623,0.13524927438582435,0.13574996042782578,0.1362408514954958,0.13671963310195992,0.1371845107563937,0.13763418002713362,0.13806778688350585,0.13848488077306878,0.1388853628149074,0.13926943134017358,0.13963752680527566,0.139990277856573,0.14032845005218236,0.1406528984591452,0.14096452505393434,0.1412642415709631,0.1415529381759265,0.14183145809560183,0.14210057811884752,0.1423609946991151],[0.13149639044373349,0.1307109138741015,0.12994292717327052,0.1291998163186508,0.12848921639774358,0.12781887104862294,0.12719647042455545,0.1266294714064219,0.12612490552298244,0.12568918171069546,0.12532789246543538,0.1250456329073855,0.12484584261135916,0.12473067960984119,0.12470093469773517,0.12475599210212983,0.1248938398827066,0.12511113034863958,0.12540328762607555,0.1257646566092169,0.12618868516263956,0.12666812981810283,0.12719527442653833,0.12776215127733392,0.12836075498106936,0.12898324076189774,0.12962210052358603,0.13027031194064193,0.13092145770910515,0.13156981383559088,0.13221040735735243,0.1328390451216368,0.13345231619539571,0.1340475711379805,0.13462288177756618,0.1351769853228117,0.13570921665305682,0.13621943249992366,0.13670793099344228,0.1371753697250889,0.13762268510230607,0.13805101535427597,0.13846162911409238,0.13885586106295705,0.13923505569087619,0.1396005198174157,0.13995348413589245,0.14029507370389327,0.14062628700940866,0.14094798300022793],[0.1278909225882057,0.12687884159143883,0.1258846501051024,0.12491819808953236,0.1239898205428932,0.12311015013918226,0.12228989125822937,0.12153955942463085,0.12086919343307853,0.1202880508529073,0.11980430080053475,0.11942473038976913,0.1191544826445844,0.11899684348657608,0.11895309345912053,0.11902243614115071,0.11920201003987833,0.11948698469638805,0.11987073552066081,0.12034508625550142,0.12090060360336136,0.12152692586302395,0.12221310656066042,0.12294795489644669,0.12372035702992899,0.12451956534477937,0.12533544639511116,0.12615868182372683,0.12698091983982293,0.12779487764748068,0.12859439743189685,0.12937446012829334,0.13013116226742957,0.13086166179233927,0.13156409896525592,0.13223749842042784,0.13288165814492853,0.13349703074805355,0.13408460185822582,0.13464576989966015,0.13518223087512096,0.13569587113541404,0.13618867046667635,0.13666261718741016,0.137119636332387,0.13756153142377328,0.13798993980436736,0.13840630104585205,0.1388118375564809,0.13920754620478676],[0.12376126963686296,0.12246792303852658,0.12119043239043754,0.11994174324528722,0.11873569185040361,0.11758676936788474,0.1165098181131391,0.11551966182694837,0.11463067788924726,0.11385632624782555,0.11320865698570576,0.11269782488185547,0.11233164382421691,0.1121152153302825,0.11205066286461399,0.11213699688343191,0.11237012515478798,0.1127430102464844,0.11324596301012549,0.11386704938256431,0.11459257948235797,0.1154076437112517,0.11629666047507914,0.11724390359631687,0.11823398342731249,0.11925226286667441,0.12028519682434685,0.1213205903445246,0.12234777608389266,0.1233577159641289,0.12434303460947085,0.125297993820367,0.1262184180632817,0.12710158102029886,0.1279460628563416,0.12875158719706067,0.12951884598904775,0.13024931951569976,0.13094509791332462,0.1316087095967435,0.13224296107237385,0.13285079169489278,0.13343514601659537,0.13399886549545462,0.13454460048224767,0.1350747426166225,0.13559137704660923,0.13609625326567815,0.13659077285311394,0.1370759920193484],[0.11913808933025175,0.11750120734954193,0.11587388264004585,0.11427276645688406,0.11271607294171725,0.11122331493941623,0.10981492445261345,0.10851175093969129,0.10733444032564696,0.10630271072685538,0.1054345565727382,0.10474542904141612,0.10424745449667978,0.1039487603775904,0.1038529766062218,0.10395896843237816,0.10426083454637389,0.10474817569850126,0.10540660925908561,0.10621847978566719,0.10716369909695848,0.1082206435453823,0.10936704048137548,0.11058078770118118,0.11184066547948351,0.11312691729585267,0.11442169011081538,0.11570933666192766,0.11697659033294065,0.1182126279801708,0.11940903832028812,0.12055971383759682,0.12166068334063097,0.1227099008308356,0.12370700462267757,0.12465305891123041,0.12555028834137566,0.12640181463242756,0.1272114029434128,0.12798322439305404,0.1287216399348803,0.12943100959959264,0.1301155299368872,0.1307791013186166,0.13142522562294376,0.13205693373677094,0.13267674133035198,0.13328663051346604,0.13388805431105444,0.1344819604213655],[0.11410749229660992,0.1120600101408599,0.11000889644335617,0.10797486996405023,0.1059812691555534,0.10405383247082878,0.10222029674297357,0.10050978135966962,0.09895193788271932,0.09757586653961821,0.09640883312536011,0.09547485974050314,0.09479330380935479,0.09437757153627571,0.09423412259557072,0.0943619037208547,0.09475229905467099,0.09538961377813455,0.09625203167624923,0.09731292564473785,0.09854236611627744,0.09990866978180711,0.10137985431328371,0.10292490315049588,0.1045147863051625,0.10612321996174955,0.10772717496873072,0.10930716130152605,0.11084732372189138,0.1123353855981437,0.11376247564159113,0.1151228681437865,0.11641366254523011,0.11763442365263196,0.11878679994766807,0.11987413430663045,0.1209010790157092,0.12187322507060148,0.12279675421115506,0.12367812078922173,0.12452376926021742,0.125339891731142,0.12613222854619005,0.12690591335126933,0.12766536249816668,0.12841420710441792,0.12915526466658753,0.12989054592096222,0.13062129172868162,0.1313480341778824],[0.10883071482807798,0.10630727941807629,0.10375679184970935,0.10120370332371616,0.098676605300499,0.09620823117754604,0.0938352134199933,0.09159750692651289,0.08953738945037651,0.0876979710035159,0.08612119637042297,0.08484541328183133,0.08390269605889505,0.08331623435009801,0.08309817540140661,0.08324830059734241,0.08375380095557863,0.08459021428529526,0.08572336254865882,0.08711195668750929,0.08871046641550054,0.0904718866808735,0.09235013554695694,0.0943019425703448,0.09628819495719797,0.09827478283171956,0.10023302365760853,0.10213975725272963,0.10397719734686212,0.105732612108133,0.1073978904966714,0.10896903702886822,0.11044562598238904,0.11183023751976066,0.11312789234293114,0.11434549775347634,0.11549131576948257,0.11657446266629548,0.11760444847222372,0.11859076417173606,0.11954252336970377,0.12046816379000366,0.12137521217515478,0.12227011398072879,0.12315812686334571,0.1240432745420769,0.12492835538524297,0.12581499823421136,0.1267037566702687,0.12759423223967667],[0.10356242717468817,0.1005117663107849,0.09739710455869918,0.09424489500408187,0.0910875764230101,0.08796411230821162,0.0849203175763427,0.08200880044866528,0.07928828816295856,0.07682206373789661,0.07467525657208905,0.07291085654690928,0.07158460386557029,0.07073932828838272,0.07039974069831324,0.07056888222816605,0.07122720169296243,0.07233456468548162,0.07383468068010712,0.07566085788665451,0.07774188217310245,0.08000710348974799,0.08239026579183091,0.08483201594785349,0.08728127219086157,0.0896957272674218,0.09204175701672637,0.09429395461019645,0.09643444971278144,0.09845211814264257,0.10034174705160136,0.10210319301848103,0.10374055327172943,0.10526136071256226,0.10667580905454051,0.10799601332829095,0.10923531178885575,0.11040761682812839,0.11152682401662711,0.11260628927098962,0.11365838396259649,0.11469413635782566,0.11572296514104015,0.11675250715470353,0.1177885372994234,0.11883497426674215,0.1198939619319702,0.12096601323679855,0.12205020152115931,0.12314438362464206],[0.0986590958074995,0.09506406891233943,0.09135351396840034,0.08755213719827534,0.08369212798054665,0.07981455109071345,0.07597082523418465,0.07222412136321212,0.06865034496063252,0.06533811153164551,0.062386815103639734,0.059901673208992354,0.05798483999935243,0.05672274614680325,0.056171848770814964,0.056347057600017625,0.05721741589081842,0.05871105456757662,0.06072739692500558,0.06315198738467805,0.06586960727343852,0.06877345314511145,0.07177022779153082,0.07478209231227094,0.07774663932728308,0.08061581875237331,0.08335442272886406,0.08593846930710848,0.08835364776039983,0.09059388608945061,0.09266004846813349,0.09455874699368164,0.0963012450203066,0.09790243087295435,0.09937984657369422,0.10075276397545102,0.10204130892179945,0.10326564166673428,0.10444520788508493,0.1055980783996207,0.10674039667329913,0.10788595093407016,0.10904588272987695,0.11022853643339221,0.11143944578358553,0.11268144519939721,0.11395488650224898,0.11525793672481767,0.11658693031912645,0.11793674930175357],[0.09456215185207488,0.09046598973865494,0.08619339709183856,0.08176218342724115,0.07719753078480118,0.07253401676093636,0.06781826081309089,0.0631123540450676,0.0584981612541852,0.054082292690917154,0.050000751272796976,0.04642056321217863,0.04353300972217592,0.041531121453887036,0.04056819849397587,0.04070923472091825,0.041903465882703377,0.04399898175985094,0.046788861714955866,0.050059095632731844,0.053618857078490074,0.05731211264584607,0.06101784163899743,0.06464555257074694,0.06812982891863481,0.07142541996266433,0.07450326636931581,0.07734740367679316,0.07995255835128123,0.08232224537644074,0.08446720793133065,0.08640407671131918,0.08815415942584989,0.08974229880004768,0.09119576123444441,0.09254313946732724,0.09381327175167152,0.09503419689107699,0.09623217785594207,0.09743083506162332,0.09865043228984628,0.09990735295937213,0.10121379249485735,0.10257767574079443,0.10400278959965367,0.1054891035943475,0.10703323769350899,0.1086290292499623,0.11026814969033452,0.11194072583424057],[0.09173757306029799,0.08726636272600027,0.08256340790463847,0.0776364560344728,0.07249835020381662,0.06716855924974587,0.06167538848309113,0.05605932121162621,0.05037829713564648,0.04471637266012477,0.03919824931002071,0.03401327597634814,0.029450801317157736,0.025931827382274654,0.023966314953978714,0.02392467539863741,0.025741458042729096,0.028951441417015313,0.03300861089172481,0.037487268317348534,0.042102906581057156,0.046673337055403635,0.051082151998224634,0.055254994219990174,0.059145475752410075,0.06272689091643024,0.06598721650836267,0.06892596251888616,0.07155206742019142,0.0738823765465282,0.07594042801374458,0.07775537300832727,0.07936091708875463,0.0807942087017308,0.08209463275884764,0.08330249738167801,0.08445763328972987,0.08559795686382458,0.0867580758687681,0.08796803551641713,0.08925230633996127,0.09062910091097942,0.09211007472748899,0.09370042341481262,0.09539934289009783,0.09720078102306536,0.09909438567814612,0.10106654748374234,0.10310144438671953,0.10518201415173059],[0.09056695112465815,0.08592854240881126,0.08102972296270664,0.0758714799194521,0.07045762009890877,0.06479527333248884,0.05889549646594292,0.05277404013977669,0.0464524135316571,0.03995956745370546,0.033335038393043914,0.02663608929229289,0.01995800683678242,0.013510233332046864,0.008020973153915178,0.006552024049538051,0.010676252503246919,0.016422021100298983,0.02234702590872058,0.02811584090655121,0.033604767367268716,0.03875069003579882,0.043516471606170094,0.04788025113101487,0.051831335954203625,0.05536834431165892,0.058498243424705575,0.061235778352107514,0.06360306638724428,0.06562923097471693,0.06734998371101106,0.06880707318535025,0.0700475224546028,0.07112258300603627,0.07208635017207396,0.07299401959540083,0.07389981954395206,0.07485472602203228,0.07590414370856197,0.07708579397873748,0.07842806725006879,0.07994905468406273,0.08165637682228694,0.08354779844607488,0.08561249672918313,0.08783276691507098,0.09018592247697575,0.09264617055552733,0.09518629985606358,0.09777908508372037],[0.09122396696494908,0.0866680106487009,0.08186260273886789,0.07681055809997181,0.0715179871108215,0.06599499817412488,0.06025661889682037,0.05432408858795688,0.04822683413903717,0.04200581119080171,0.03571981925983298,0.029458933939703818,0.023376772938219176,0.01777697026127422,0.013345483727259282,0.011458948179393724,0.013070283296184917,0.016986547255007273,0.021761830318735773,0.026705418581615632,0.03152032032461648,0.03606267970394488,0.040254320599052894,0.04405060526692676,0.04742738902624426,0.050375206254155376,0.05289650407107187,0.0550042898068615,0.0567214785744232,0.05808058011260264,0.0591234974368331,0.0599012486737506,0.060473419205580047,0.06090713301071102,0.061275326759651375,0.061654149701113034,0.062119429640202645,0.062742357071952,0.06358481867594341,0.06469506810362993,0.06610452443588016,0.06782633617803983,0.06985595698160206,0.07217349880061415,0.07474725906018033,0.0775376867938092,0.08050115130111332,0.08359310356157411,0.08677046022827292,0.08999322056779308],[0.09360685061912907,0.08935978793089845,0.0849071233723909,0.08025954030169158,0.07543300735638507,0.07045015367728101,0.065342120860957,0.06015112106241068,0.05493404398685194,0.04976758901054139,0.04475545667703492,0.04003775598437139,0.03580092283861702,0.03228092170114151,0.02974198658980537,0.028408172350131947,0.028358333072878255,0.029464309801184006,0.03144165543703379,0.033962952971593505,0.03674043821199432,0.03955301098004115,0.04224157316460636,0.0446956202187892,0.046840946651071094,0.04863073698756324,0.05003972865554226,0.051060649361770884,0.051702245972932534,0.05198841472500006,0.051958075532969036,0.05166547923408466,0.05118059070785837,0.05058905220906614,0.04999101993599796,0.049497966424288956,0.04922655067203346,0.04928918025877109,0.04978212988478095,0.050773730361128776,0.05229616026460316,0.05434362972545054,0.05687730285224301,0.059834729165561304,0.06314048342483661,0.06671537782838977,0.07048303695318142,0.07437381944429261,0.07832666572729648,0.08228956654359497],[0.0973755722656147,0.0935894913903811,0.0896544894733953,0.08558836485251563,0.08141488929958626,0.07716497196853038,0.07287799174192255,0.06860325715477884,0.06440146614968734,0.06034587083587402,0.05652256575945393,0.05302890192219014,0.04996859771064843,0.04744206989958832,0.045531577834193294,0.0442835193541202,0.04369369740467163,0.04370250233900457,0.04420314996059717,0.04505948228247509,0.04612589457299765,0.04726322317137192,0.0483483503405909,0.04927837524038996,0.04997132327098004,0.05036518304473118,0.05041647131761655,0.05009901062890303,0.04940328542817715,0.04833659189251181,0.046924153921679264,0.04521138401392897,0.04326745091007343,0.041190142030358895,0.03911139963336396,0.03720138518829431,0.035666083729443646,0.03473036267502692,0.034600093138545264,0.03541056372206102,0.037188258127010536,0.039852559310226146,0.04325375597417531,0.04721914613445385,0.05158515915726356,0.0562118186374727,0.0609855553801484,0.0658167204929664,0.07063556020943328,0.0753882955873398],[0.10206690016793019,0.0988069868294033,0.0954498244824119,0.0920159047673519,0.08853067824243739,0.08502502486501534,0.08153558706639336,0.07810484332993904,0.07478074822920633,0.07161571186252212,0.06866466001777465,0.06598194737626303,0.0636170450521124,0.06160923331411298,0.059981974226602675,0.0587380655968252,0.0578568276965388,0.05729423374826436,0.056986108175131986,0.05685363745037798,0.05680990283980627,0.056766152339175785,0.05663694733510539,0.05634385353175776,0.05581776351531218,0.05500016096011202,0.053843698602018084,0.05231243739667497,0.05038204816763594,0.048040255353799334,0.04528784181666345,0.04214068345718122,0.038633640888072425,0.034827916072952755,0.030825123129687777,0.026794485433592755,0.023023550026724175,0.0199942736962945,0.018404201507241574,0.018877840359133435,0.021431110733079812,0.02551061779840091,0.03051322332159478,0.03602097789322708,0.041776625588632654,0.047620589129344804,0.053449331540634346,0.05919253728836546,0.06480081974917072,0.07023885666525166],[0.10721519943047123,0.10447760114625344,0.10168123976556055,0.09884533622667105,0.0959924284949409,0.09314831328434982,0.09034177644906902,0.0876040389813227,0.0849678436743479,0.08246612061659939,0.08013020613464414,0.0779876559366914,0.07605978784577004,0.07435919767157098,0.07288758199119551,0.07163423266100623,0.07057550704479706,0.06967542347856862,0.06888732327082724,0.06815634628257103,0.06742234940286994,0.0666228831129099,0.06569591490662192,0.064582107186708,0.06322657732790997,0.061580160251543045,0.059600249542688256,0.057251315999428246,0.05450520263505648,0.051341282940098536,0.04774655270136142,0.043715710375450384,0.03925127127250831,0.034363763282591796,0.029072086145303374,0.023404260015659477,0.017399439455986092,0.011116207455481978,0.004708851935980792,0.0028445924564589253,0.009360489873444705,0.01622997128114702,0.023126020384120698,0.029972582605378197,0.03671918522771375,0.04332603609713551,0.0497608220468053,0.05599742594951634,0.06201513308602183,0.06779800616332168],[0.11242982330912411,0.11016885083554677,0.10787394040726293,0.105560975336303,0.10324770126995277,0.10095343358238876,0.09869859676181057,0.09650407145034322,0.09439033629936297,0.09237641136745868,0.09047863765857345,0.08870936145914625,0.08707562709492779,0.08557800925429432,0.08420972643989702,0.08295616270606962,0.08179488371354941,0.08069617157186099,0.07962403451451959,0.07853758860842967,0.07739267277780743,0.07614355115190914,0.0747445753207053,0.07315171476992284,0.07132390614903593,0.0692242127190423,0.06682081999195322,0.06408792233563622,0.06100658256051917,0.05756568137665381,0.05376313298866883,0.04960766028875094,0.04512167026683458,0.040346315773593,0.035351086716756484,0.030253265568975566,0.02525956459761184,0.02075483076218926,0.017450539606249427,0.016372099051513576,0.018083602320739724,0.02199494360221516,0.027156745443417275,0.03293252614251703,0.03897582941876693,0.04509541720552513,0.05117778833213575,0.05715063015440801,0.06296543893849037,0.06858873449537763],[0.1174237440809059,0.11557472979109354,0.11370585874270188,0.11182916668006236,0.10995753775614323,0.1081043683219576,0.10628312428366118,0.10450679115574206,0.1027872258339256,0.10113443168439,0.09955579273636647,0.09805531664191484,0.09663294696078872,0.09528401030543056,0.09399886052675537,0.09276276943953486,0.09155609266294693,0.09035471322774848,0.0891307393942439,0.08785341158010261,0.08649016023643695,0.0850077537172402,0.08337348224822311,0.08155633898449077,0.07952817920357394,0.07726486168569711,0.07474740129995742,0.07196318952786313,0.06890737302991853,0.06558452476892249,0.0620108056825193,0.058216907310459094,0.05425219335755099,0.05019060207665065,0.04613891845396161,0.04224757795781821,0.038722143412203126,0.03582796480066386,0.03387053630353306,0.03313013513512128,0.03375976729991973,0.03571635749635242,0.03879109349334996,0.042706182281132384,0.04719705170800906,0.05204793416573981,0.05709516477720215,0.06221823703832858,0.06732924310887084,0.07236416993424132],[0.12201020981136482,0.12050430195568716,0.11898533436777047,0.11746183264653424,0.11594256016471846,0.1144362227688147,0.11295111398067263,0.11149470747468757,0.11007320973836603,0.10869109247297144,0.10735063069318826,0.1060514776559511,0.10479031062759263,0.10356058117266416,0.10235239961304467,0.10115257568407479,0.09994482704283164,0.09871015562009264,0.09742738065397831,0.09607380836285109,0.09462601296183755,0.09306070280514596,0.09135564885147378,0.08949065984857776,0.08744859875206629,0.08521644701927751,0.08278643675448157,0.08015728452051073,0.07733557402284869,0.07433734575754837,0.07118995513285334,0.06793424521366477,0.06462702242660762,0.06134367864854949,0.058180499035577385,0.0552556484159418,0.05270703664619662,0.05068454139494632,0.04933437712625864,0.048776166517249565,0.04907864412567228,0.050244286228276355,0.05221084214287913,0.054868620163031775,0.05808438436550619,0.061722303723396967,0.0656574169101773,0.06978188712550942,0.07400637365283724,0.07825882187783305],[0.12608495812541587,0.1248570740435288,0.12361847344477758,0.12237483206654494,0.12113174133242964,0.11989447843005721,0.11866774650372888,0.11745539270606901,0.11626011525914867,0.11508317396311163,0.11392412135541195,0.11278057353159927,0.11164804009707305,0.11051983156559415,0.10938705970068963,0.10823874201408652,0.10706201635021148,0.10584246585200593,0.10456454936096962,0.10321212814614168,0.10176907730385226,0.10021996948631748,0.09855081977535121,0.09674988321291468,0.09480850018704154,0.09272198878601774,0.090490586361995,0.08812044349581871,0.08562467029723585,0.08302442443287379,0.08035000783372409,0.07764189821807942,0.07495157459883828,0.07234189675777938,0.069886670999063,0.0676689076984478,0.06577722650112726,0.06430002450530033,0.0633175335675311,0.06289276633978026,0.06306328425393022,0.06383610108774986,0.06518734949067796,0.06706674919318148,0.0694053143953923,0.07212402084574258,0.0751415001621611,0.07837973964273538,0.08176763100698607,0.08524272521473582],[0.1296050511326906,0.12859730446005954,0.1275786856251964,0.126552716281343,0.12552269450780712,0.12449152853016607,0.12346155762831593,0.12243436679825927,0.1214106035469292,0.12038980678688024,0.11937025896422826,0.11834887311439089,0.11732112635397143,0.11628105031516614,0.11522128724003282,0.1141332180100943,0.1130071655208545,0.11183267381328263,0.11059886055484812,0.10929483809502942,0.10791019659195462,0.1064355416802404,0.10486307873798192,0.10318723576564473,0.10140531679954543,0.09951817706633909,0.09753090897878462,0.09545352361306914,0.09330160432729445,0.09109689637491869,0.08886777753087058,0.08664952935542544,0.08448429806920303,0.0824206030939423,0.08051223119010464,0.07881636360563062,0.0773908474846872,0.07629066230836698,0.07556384636418222,0.0752473918387657,0.0753637948670726,0.07591894739143208,0.07690182430544334,0.07828601016241343,0.08003268461621242,0.08209441396833991,0.08441905623497438,0.08695323902160207,0.08964510628159736,0.0924462509888564],[0.1325696425352177,0.13173217166802914,0.13088236759975494,0.13002220094584946,0.12915338566149295,0.12827726586050492,0.12739469908734385,0.12650594103980112,0.1256105376852675,0.12470723146630065,0.12379388875927175,0.12286745585423674,0.12192395041224349,0.12095849461261984,0.11996539505547549,0.118938273005027,0.11787024685391785,0.11675416688369203,0.11558290061713525,0.11434966540512129,0.11304840341822064,0.11167419291141775,0.11022368841204067,0.10869558117801434,0.10709106963798865,0.10541432724035067,0.1036729518427953,0.10187837610552578,0.10004621202844914,0.09819649474004423,0.09635378130230367,0.09454705082684185,0.09280934496661428,0.09117708672268952,0.0896890258021719,0.0883847863436012,0.08730304186616213,0.08647941170928876,0.08594425285071317,0.08572059019228874,0.08582246025140187,0.0862539152070705,0.08700884168198258,0.08807161183471542,0.08941844300660257,0.09101923803743696,0.0928396365385002,0.09484302793131144,0.09699234004336872,0.09925149553434083],[0.13500456844296704,0.13429505509927198,0.13357107562342374,0.13283351797531642,0.13208303635958565,0.13131997933397896,0.13054431910522513,0.12975558561456085,0.12895280949284035,0.12813447830332647,0.12729851064436104,0.1264422526187839,0.12556250087099355,0.12465555584244904,0.12371730811786075,0.12274335976051709,0.12172918141223228,0.12067030471273092,0.1195625483223467,0.11840227454408668,0.11718667224662617,0.11591406046898908,0.11458420568814515,0.11319864416971791,0.11176099899532498,0.11027727916014357,0.10875614547938545,0.10720912492113262,0.10565075151722199,0.10409860852987174,0.10257324371257183,0.1010979283289351,0.09969823251814033,0.09840139634460625,0.09723548911076582,0.096228370220505,0.09540649245830529,0.0947936199524391,0.09440956246883611,0.09426904711112086,0.09438085012474037,0.09474729064238017,0.09536414613508049,0.09622099403061321,0.09730192797690292,0.09858655333749823,0.10005114325436894,0.10166983591569816,0.10341577131889124,0.10526209414656659],[0.13695097772598358,0.13633363380190375,0.1356992804690558,0.1350480559260544,0.13437991250628992,0.13369457580056338,0.13299150721354897,0.1322698724591565,0.1315285187216626,0.1307659633340047,0.12998039682962262,0.12916970309267603,0.12833149905349653,0.12746319595014888,0.12656208360970592,0.125625438508174,0.12465065556457906,0.12363540273254968,0.12257779648927518,0.12147659529811568,0.12033140703931287,0.1191429052547952,0.1179130478207769,0.11664529032482296,0.11534478496726816,0.11401855423600335,0.11267562696560973,0.11132712280062443,0.1099862697483007,0.10866833876070965,0.10739047959700405,0.10617144417087364,0.1050311878245727,0.10399034604214824,0.10306959427046108,0.1022889114328553,0.10166678224595482,0.1012193874992104,0.10095984218909376,0.10089754577935459,0.10103770453296969,0.10138107209937217,0.10192393282851621,0.10265832622176985,0.10357248534734169,0.10465144162661097,0.10587773635708504,0.10723217669895857,0.10869457949671446,0.11024445767505857],[0.13845751330210168,0.13790197464228005,0.13732651055860326,0.13673072302811928,0.13611408263711924,0.1354759107133089,0.13481536588486595,0.13413143676281863,0.13342294252057021,0.13268854315298187,0.13192676112547252,0.13113601596223584,0.13031467306664102,0.12946110771479788,0.1285737847175299,0.12765135371214334,0.12669275943102476,0.1256973656076455,0.12466509042987765,0.12359655064205909,0.12249321053580159,0.12135753115941944,0.12019311412362098,0.11900483340043873,0.1177989475312233,0.11658318372945915,0.1153667845711597,0.1141605074406759,0.112976566826328,0.11182851017354047,0.11073101957511024,0.10969963438121302,0.10875039405534058,0.10789940634413263,0.10716235287091326,0.10655395205979837,0.10608740692112213,0.10577387143154993,0.1056219726508368,0.10563742514901364,0.1058227691440349,0.1061772541875251,0.10669687743815588,0.10737457143172423,0.10820052301683519,0.10916259477687751,0.11024681411973847,0.11143789368248658,0.11271974928612533,0.11407598728589965],[0.13957532540847659,0.1390556810203373,0.138512744673607,0.1379456975962953,0.13735364004338763,0.13673559059122953,0.1360904903401269,0.1354172131625576,0.13471458312809603,0.13398140017815072,0.13321647500708597,0.13241867392604192,0.13158697423846322,0.1307205303407211,0.1298187503779494,0.1288813828367847,0.12790861194706074,0.12690116019883957,0.12586039566582724,0.12478844116905612,0.1236882816259876,0.1225638652243427,0.1214201933583712,0.12026339359998543,0.1191007693955526,0.11794081974869948,0.11679322196197765,0.11566877068319134,0.1145792671752134,0.11353735405125148,0.11255629282838757,0.11164968464054482,0.11083113831317519,0.11011389458614619,0.10951042024221405,0.10903199072015035,0.10868828376397945,0.10848700901563009,0.10843359851665864,0.10853098043143265,0.10877945294781304,0.10917666775563899,0.10971772369496052,0.11039536231689202,0.11120024942933394,0.1121213211740823,0.11314617033144132,0.11426144840876784,0.11545326124717131,0.11670753970613716],[0.14035518022215257,0.1398492390310762,0.13931607288420952,0.13875448099220514,0.13816322176524573,0.13754102512871497,0.1368866101530845,0.13619870879086413,0.13547609645964764,0.13471763011339208,0.13392229429906016,0.13308925549847703,0.13221792480260586,0.13130802865553537,0.13035968703772668,0.12937349803339354,0.12835062724786878,0.12729290001213336,0.1262028937407795,0.12508402720781228,0.12394064288852592,0.1227780779094115,0.12160271858607323,0.12042203305905409,0.11924457622295886,0.11807996106681455,0.11693879080203756,0.11583254686004067,0.11477342910739541,0.11377414654812067,0.1128476594105902,0.11200687682159305,0.1112643181077051,0.11063174984734338,0.1101198146915264,0.10973767112733182,0.10949266518430406,0.10939005506294489,0.10943280748359861,0.10962148021998722,0.10995419917352826,0.11042673117956832,0.111032646444259,0.11176355804614764,0.11260942108612639,0.11355887130541167,0.11459958241230885,0.1157186227226711,0.11690279454575288,0.11813894344930706],[0.14084599624446895,0.14033481714145282,0.13979181400799706,0.1392153858341646,0.13860391690048363,0.13795579910549602,0.13726946016952396,0.13654339835224064,0.13577622424681562,0.13496671009848202,0.13411384693492395,0.13321690958469876,0.13227552939315426,0.13128977411871712,0.13026023410262627,0.12918811335007918,0.1280753236402848,0.12692457920000919,0.12573948883727307,0.12452464175285477,0.12328568255021387,0.12202937028486478,0.12076361578359288,0.11949749099337306,0.11824120388277255,0.11700603253066473,0.11580421263182902,0.11464877386643238,0.11355332254591267,0.11253177074059705,0.11159801570629338,0.11076557771798783,0.1100472090799714,0.10945449162385,0.10899744378910861,0.10868416069931608,0.1085205108644586,0.10850991085243591,0.10865319445383069,0.10894858593869103,0.10939177881330049,0.10997611313448184,0.11069283706889119,0.11153143292789772,0.11247998491117751,0.1135255653437869,0.11465461797255903,0.1158533203011131,0.11710791127942127,0.11840497525129177],[0.14109423987149033,0.14056190255230427,0.13999243100571265,0.13938376741701056,0.1387338486512226,0.13804063612272907,0.1373021523317605,0.13651652471934125,0.13568203742225896,0.13479719140022026,0.1338607732511928,0.13287193281996154,0.13183026943043155,0.13073592622491334,0.12958969166405943,0.12839310672019236,0.1271485756767832,0.1258594777231939,0.12453027570737524,0.12316661748999883,0.12177542435536157,0.12036495992131861,0.11894487202383884,0.1175261992381246,0.11612133318581765,0.1147439277590919,0.11340874709825943,0.11213144583971495,0.11092827803562666,0.10981573538472453,0.10881012099150433,0.10792707152545515,0.10718104779954536,0.10658482051364686,0.10614898305018762,0.10588152555043391,0.10578750306473034,0.10586882493886947,0.10612418313727583,0.10654912509958378,0.10713626378198646,0.1078756057544415,0.10875496933979158,0.10976045985751087,0.11087696830137447,0.11208866269723507,0.11337944690040842,0.11473336845785062,0.11613496423072427,0.11756953887994676],[0.14114371870482645,0.14057727928513308,0.13996771932163105,0.13931244752558652,0.13860885824887417,0.13785436644396146,0.13704645024336576,0.13618270196764037,0.13526088833494002,0.1342790205726017,0.13323543501222523,0.13212888457266478,0.13095864128607276,0.1297246096839595,0.12842745041383838,0.12706871288061505,0.12565097497704106,0.12417798706088322,0.12265481623261597,0.12108798565423814,0.11948560213098927,0.11785746348440815,0.11621513545131203,0.1145719860851395,0.11294316413389452,0.11134550694596253,0.10979736354591299,0.10831832015621895,0.1069288191820775,0.10564966900586338,0.10450145106653037,0.10350384233682393,0.10267488444577515,0.10203024349214142,0.10158251454352449,0.10134062919273444,0.10130942117085626,0.10148939309882204,0.10187670814745158,0.10246340674801953,0.10323782483979903,0.10418517076358057,0.10528820593117123,0.10652797101377127,0.10788450381910687,0.1093375050780622,0.11086692127540247,0.11245342687900811,0.1140787999808301,0.11572619443545057],[0.14103542264056937,0.14042497268314202,0.13976486784102868,0.13905190546506882,0.1382828405923097,0.13745442321623252,0.13656344410281115,0.13560679021748476,0.13458151085671025,0.13348489557939913,0.13231456499738856,0.13106857539590955,0.12974553799625946,0.12834475341965762,0.12686636153314848,0.12531150631735608,0.12368251464529363,0.12198308684600123,0.1202184955837512,0.11839578784653546,0.11652398264486184,0.11461425433184931,0.11268008827232945,0.11073739200148704,0.10880454125325133,0.10690233674786621,0.10505384513611694,0.10328409707222605,0.10161961841365007,0.10008777856214147,0.0987159542733779,0.09753052831283661,0.09655576890336412,0.0958126644481605,0.09531781258557495,0.0950824759320454,0.09511191242844122,0.09540506318679966,0.09595463800996037,0.09674758690096767,0.0977658966394011,0.09898761573154871,0.10038799506437987,0.10194063568828372,0.10361855455479593,0.1053951065111952,0.10724472940453725,0.1091435037600035,0.11106953666761969,0.11300319085069248],[0.1408071830482188,0.14014591278260974,0.1394281248569755,0.13864994545908346,0.13780741312767672,0.1368965151714177,0.13591323326672364,0.1348535995814314,0.13371376488751074,0.132490080234744,0.13117919384980767,0.12977816498901623,0.12828459649012483,0.12669678771361606,0.1250139094012759,0.12323620166056722,0.12136519574065423,0.1194039594105537,0.11735736446460643,0.11523237301555872,0.11303833660735152,0.11078729857629324,0.10849428529131902,0.10617756573277033,0.1038588512794282,0.1015633988124652,0.09931997109247725,0.09716060044759918,0.09512009791195693,0.09323525414595497,0.09154369571831249,0.09008239515523447,0.08888588710270848,0.08798431123331941,0.08740147155854724,0.08715315004752824,0.08724591685901836,0.0876766264565305,0.08843268420564501,0.08949303858209265,0.09082973767072258,0.09240981727744718,0.09419727480596916,0.09615491992612303,0.09824595858735528,0.10043523794570491,0.10269013963763486,0.10498115003649734,0.1072821585563469,0.10957054268020375],[0.14049305402342224,0.13977721448553188,0.13899795778284038,0.1381507152415363,0.13723077218927301,0.13623330030438438,0.13515339922318167,0.1339861489661624,0.13272667495047177,0.1313702275818093,0.12991227866216826,0.12834863710562486,0.12667558671389528,0.12489004901112526,0.12298977434797242,0.12097356461825823,0.11884153092487822,0.11659538929011909,0.11423879688638003,0.11177773005574586,0.10922090328543184,0.1065802248786105,0.10387127971614522,0.10111382148003319,0.09833224510044285,0.09555599410408608,0.09281983648456828,0.09016391734657088,0.08763347000728955,0.08527804679631479,0.08315012962588712,0.08130301723543844,0.07978798022666934,0.07865083448027835,0.07792828714998974,0.07764459512066517,0.0778091526670307,0.07841551871167743,0.07944210469128433,0.08085436809845456,0.08260804123510761,0.08465278126779956,0.08693567496783856,0.0894042050462334,0.09200849226372304,0.09470279879553506,0.0974463851469626,0.10020385910632784,0.10294515930559807,0.10564529750589835],[0.14012246373558113,0.13935113551338985,0.1385097791114681,0.13759315677153716,0.13659582084855815,0.1355121394832909,0.13433633092264344,0.1330625081084361,0.1316847354248904,0.13019709981032204,0.12859379880632907,0.12686924854569562,0.12501821517563347,0.12303597378194919,0.12091849952515862,0.1186626964177006,0.11626666994571765,0.11373005052973632,0.1110543755454851,0.10824353813806734,0.10530431108914298,0.10224695306806417,0.09908590192093085,0.0958405539246453,0.09253611709519935,0.08920450759050073,0.08588522669177004,0.08262610666708184,0.07948374286688302,0.07652333819167405,0.07381759104495425,0.07144420369503071,0.06948165669085701,0.06800318930038847,0.06706949746030556,0.06672138914975678,0.06697416297172167,0.0678153544665,0.06920657596340295,0.07108886188840026,0.07338993767330171,0.07603161757142554,0.0789360116063626,0.0820299516529236,0.08524764809173134,0.08853191440158638,0.09183438612100561,0.09511511494187379,0.09834182467790113,0.10148902233500998],[0.139719321445729,0.1388939357993393,0.1379925036944878,0.13700919805346137,0.13593792227534313,0.13477232802883407,0.1335058404832961,0.13213169246797624,0.13064296933093103,0.12903266661061588,0.12729376304892473,0.12541931198284212,0.12340255477587928,0.12123706071924306,0.11891689878300926,0.11643684777535668,0.11379265292962948,0.11098133875166447,0.10800159019802866,0.10485421699115169,0.10154271915143284,0.09807397558988448,0.09445908158684864,0.0907143644231236,0.08686260755478678,0.0829345087505466,0.07897037899898492,0.07502204266523724,0.07115480125884467,0.06744913770424461,0.06400152744063875,0.06092328740717769,0.05833597090071339,0.05636182016412985,0.05510891145940117,0.05465329064146447,0.0550235952834141,0.05619462324258558,0.058092950425446634,0.06061189655346245,0.06362946917276542,0.0670235912366178,0.07068206263662724,0.07450747603995919,0.07841854493810226,0.08234936399470673,0.08624771068640795,0.09007305389714435,0.09379461299009077,0.09738961635407753],[0.13930136528072276,0.1384249861797976,0.13746735812571537,0.13642219085999902,0.1352828792862122,0.13404251412214122,0.13269389850574995,0.13122957176482297,0.1296418418001392,0.12792282782876402,0.1260645156035639,0.12405882768863019,0.12189771195660211,0.11957325222206219,0.11707780588914123,0.11440417474657975,0.11154581669592123,0.10849710839937414,0.10525367179996173,0.10181278150999286,0.0981738756342777,0.09433920033433839,0.0903146292468591,0.0861107139366931,0.08174404229847917,0.07723900936295154,0.07263013858638949,0.06796512428453189,0.06330877239074377,0.0587479277687363,0.05439712630364884,0.05040376903803557,0.04694962711312986,0.04424245834574131,0.042489755382793336,0.04185247656184117,0.04239437155289964,0.044058151781865784,0.046686760245899774,0.050073422429800236,0.05400897240330555,0.0583094700225493,0.06282546857300171,0.0674408726280053,0.07206781829757379,0.07664094549530308,0.08111235986757416,0.08544758555321573,0.08962243310841927,0.09362060719214965],[0.1388800593191698,0.13795651087469288,0.13694741874288532,0.13584618210712587,0.1346458618979889,0.13333918691305577,0.13191856456469403,0.13037609713789675,0.12870360460896693,0.12689265528547933,0.12493460579040447,0.12282065224462037,0.12054189492431844,0.1180894192139032,0.115454396384983,0.11262820867203525,0.10960260438044467,0.10636989049663226,0.10292317269447784,0.09925665609511107,0.0953660251953099,0.09124892894177163,0.0869056085054387,0.08233972346087166,0.07755946120380876,0.07257906220820216,0.06742097347891127,0.06211897707881787,0.05672286610054605,0.05130560233326128,0.04597439124976741,0.04088746295354369,0.03627706979655069,0.03247134990181863,0.02988416264699902,0.02891289071568305,0.029738277070202945,0.03220046770466773,0.03590876871351437,0.04044451232735814,0.045471868704886426,0.05075236860891002,0.056123770031638896,0.06147660583498668,0.06673683612186239,0.07185434291150587,0.07679547970790918,0.0815382002119216,0.08606879844430701,0.09037966598573005],[0.13846126934695568,0.13749425958830264,0.136438257763307,0.13528650372209278,0.13403190027062298,0.13266701847160003,0.1311841067430387,0.12957510436228267,0.1278316600840306,0.12594515670567896,0.12390674256849563,0.12170737117717395,0.1193378503642969,0.11678890273517409,0.11405123952336116,0.11111565049811035,0.10797311323699318,0.10461492597907404,0.1010328695160607,0.09721940533994602,0.09316791984693516,0.08887302831912904,0.08433095859302839,0.07954004447675866,0.07450137632684074,0.06921968712663575,0.0637046101013347,0.05797255686950652,0.05204969824660995,0.04597703858641966,0.03981974993124118,0.03368578369190548,0.027765771785142127,0.022420982281511875,0.018348887572826426,0.01664803119365208,0.018043283592643518,0.021915798213037158,0.02714664954752809,0.032994497014018596,0.03907374778847204,0.04518281341779487,0.051209077366028775,0.057085621404193244,0.06277111959811578,0.06823980134475063,0.07347601449352638,0.07847103966504006,0.08322108764240646,0.08772596283196817],[0.13804677005633167,0.13703919258886546,0.13593982234596053,0.13474186170782174,0.13343819897296477,0.13202141653434116,0.1304838026094991,0.12881736695165452,0.12701386102143805,0.1250648031658621,0.12296150943564925,0.1206951307790734,0.11825669748528184,0.1156371719188637,0.11282751079732929,0.10981873852214517,0.10660203339151407,0.10316882891077644,0.09951093288976495,0.09562066759949574,0.09149103499361923,0.08711591195718758,0.08249028187009297,0.0776105107512191,0.0724746794691882,0.06708298920915026,0.0614382683141647,0.055546631171205355,0.04941839002633335,0.04306944252240752,0.0365236865587934,0.029818027690381367,0.023015270786448824,0.01624765008934019,0.009928515557026795,0.0061501131006843355,0.009122575818946078,0.015267288695398451,0.021973887005656674,0.02873425806377384,0.035398562009658886,0.04189981092766017,0.04820049881006271,0.05427742440095979,0.06011594118057609,0.06570722193602047,0.0710466974147494,0.07613303506696056,0.08096740634181229,0.08555293005831188],[0.13763640967613197,0.13658998206253578,0.13544932543932933,0.13420767763276026,0.13285799998443695,0.13139299116420236,0.12980510474910656,0.12808657087943454,0.1262294223189126,0.1242255252708414,0.12206661533923191,0.11974433907917383,0.11725030166023964,0.11457612127847332,0.11171349110541405,0.10865424976672682,0.10539046160868032,0.10191450834777173,0.09821919411487617,0.09429786640376607,0.0901445560108009,0.08575413969394738,0.08112252995861893,0.0762468970576872,0.07112592893789481,0.0657601354798066,0.06015220411560604,0.0543074153505976,0.04823413065322744,0.04194437699825596,0.03545458926167342,0.02878669652516272,0.021970232706097343,0.015048733508794149,0.008116236403289056,0.0021854416579082203,0.006669016105659172,0.013542694573423546,0.020430557234259905,0.02720886502884385,0.03383109570054922,0.04026815986036737,0.04649960048134898,0.052510914553541156,0.058292219990699286,0.0638373524737746,0.06914315769678261,0.07420890714616132,0.07903581082200989,0.08362661327263],[0.1372305577586798,0.1361458824761411,0.13496461321734915,0.13368004123501767,0.13228522484552704,0.13077301041414183,0.12913605759427735,0.12736686903847075,0.12545782477198572,0.1234012213931813,0.12118931624180673,0.1188143766631057,0.1162687345001437,0.11354484598060474,0.11063535724258527,0.10753317588690664,0.10423154917710557,0.1007241498656163,0.09700517114722353,0.09306943298015712,0.08891250303615314,0.08453083692830694,0.07992194423945058,0.07508458942724512,0.07001904027371511,0.06472738193244298,0.059213923551878926,0.053485741234419536,0.04755343709152214,0.04143228157756792,0.03514414555780047,0.02872137601122593,0.022216532856847392,0.015734854212683842,0.009592380999074697,0.005482239415366806,0.007918358859637665,0.013733249001869634,0.02010509137236442,0.02653604841553831,0.03288928998436195,0.03910516502510113,0.045150576862147615,0.051005138501300874,0.05665595752473981,0.06209510802467727,0.06731815697742212,0.07232320073504225,0.07711019618019758,0.08168048472304139],[0.13683236073344585,0.13570939570951707,0.13448731425360025,0.133159431618683,0.13171887191662981,0.13015859684860068,0.1284714393863843,0.12665014255565202,0.12468740339563149,0.1225759220784931,0.12030845606684529,0.11787787907214126,0.11527724445584606,0.11249985259815094,0.10953932165999256,0.10638966110448558,0.10304534735406291,0.09950140108260529,0.09575346593637714,0.09179788902304768,0.08763180441018253,0.08325322227377083,0.07866112842313153,0.07385560196641923,0.06883796327733842,0.06361097088196867,0.05817909581795869,0.05254891867519286,0.046729726253993756,0.04073445520063306,0.03458131324617914,0.028296969381807,0.021924266880415797,0.015547110720669109,0.009411149070065034,0.004927956345567241,0.007057148586881157,0.012797968268369368,0.019046685787431825,0.025330302230593828,0.03152844593769089,0.03759099578585947,0.04349151418406964,0.04921461582159638,0.0547511020111904,0.06009556452147932,0.06524501609758895,0.0701980508217874,0.07495432108053057,0.0795142187123318],[0.13644935995340793,0.13528819486458576,0.13402512466364583,0.13265342850597042,0.13116622899376817,0.12955652863989747,0.1278172522340154,0.12594129527413256,0.12392157851381816,0.12175110853285713,0.11942304406403179,0.11693076759869353,0.1142679615485286,0.11142868796268961,0.10840747049522508,0.10519937700101656,0.10180010083265406,0.09820603865301929,0.09441436242503934,0.09042308327254339,0.08623110523831132,0.08183826775120646,0.07724537705384774,0.07245422918451475,0.06746763064555959,0.06228942794637353,0.05692456410436904,0.0513791892284084,0.04566086389109186,0.0397789092675059,0.03374498191480448,0.027574005959043003,0.02128579106871611,0.014908664656044538,0.008494520158535001,0.002367672665650985,0.004850169876045889,0.011157153347452015,0.017463669851613225,0.023667116808865768,0.029736794824094016,0.03565685963944245,0.04141829202250343,0.047015911486213396,0.052446699580920776,0.05770875219956575,0.0628006429878657,0.06772107849319535,0.07246875716775257,0.07704236255923083],[0.13609416584659098,0.1348959430554616,0.13359279893482506,0.13217790634501153,0.1306443057935618,0.12898494914648798,0.12719275046084436,0.12526064423379324,0.12318165124789111,0.1209489520397141,0.1185559678228927,0.11599644845089252,0.11326456670373095,0.11035501782219923,0.10726312279204274,0.10398493340364647,0.1005173365936373,0.09685815504166324,0.09300624049797829,0.0889615559375319,0.08472524250219263,0.08029966749903725,0.07568845075582836,0.07089646881042976,0.06592984032903847,0.0607959026934959,0.05550320026119797,0.05006152186709717,0.04448205402596942,0.0387777707858939,0.032964303333696834,0.027061871160029626,0.02110003714093065,0.015132403680188177,0.009303656285266599,0.004432411078830727,0.005341112521753999,0.010576848103299421,0.016338621640834536,0.022138737289314554,0.027879430317854264,0.033526975529237946,0.03906619450095093,0.04448883345028409,0.049789307232851465,0.0549628375346434,0.06000463143409104,0.06490959690970138,0.06967235156033788,0.07428738401302563],[0.1357840718874304,0.13455187346982622,0.13321169533853008,0.13175654433440423,0.13017930753570847,0.12847280212797538,0.12662983374044365,0.12464326377392004,0.12250608615965537,0.12021151386705234,0.11775307531198756,0.1151247205979555,0.11232093723966262,0.10933687466256777,0.10616847633278849,0.1028126178419465,0.09926724864799061,0.0955315344622292,0.09160599649661517,0.08749264299442189,0.08319508775773277,0.0787186499297445,0.07407042938903394,0.06925935328182792,0.06429619234949495,0.05919355239157774,0.05396585942328129,0.04862938288090243,0.043202393094137835,0.03770566095863272,0.03216377494117291,0.026608482498586758,0.02108762249760675,0.015692445154701726,0.010661363735655434,0.006864875229100251,0.006790967767584652,0.010463338339312605,0.015348841848311066,0.02055504492805502,0.02584918565425507,0.031151946654515997,0.03642848553667042,0.04165924903237452,0.04683014776931868,0.05192881596838431,0.056943213254526164,0.06186124836184451,0.06667086338034203,0.0713603065556383],[0.1355396781872168,0.13427921418922345,0.13290797727397557,0.13141877743037586,0.12980430667202805,0.128057193349494,0.12617006614114754,0.1241356284985476,0.12194674428012353,0.11959653523302921,0.1170784908680905,0.1143865911055072,0.11151544183563179,0.10846042322228364,0.10521785015513233,0.10178514370716096,0.09816101174393321,0.09434563592916131,0.09034086124026315,0.08615038271428985,0.08177992246746069,0.07723738808383848,0.07253300133984292,0.06767938417521724,0.06269158742799837,0.05758704840005987,0.05238546852909101,0.04710861813744378,0.04178011438473501,0.0364253121199115,0.031071676987886584,0.025750622284170042,0.020503660925505405,0.0154026205151927,0.01062572603939687,0.006807006616588824,0.006028804898701357,0.009046137958433762,0.013487594082378986,0.018331158812607273,0.023321939915293466,0.02838023483414786,0.033472240230706274,0.03857720863696356,0.04367739603304575,0.04875494177263415,0.05379123514502249,0.0587672099482448,0.06366393368155128,0.06846321808874795],[0.13538274853436147,0.13410271557941061,0.13270976649865732,0.1311965267209982,0.12955549779771466,0.12777911413340087,0.12585981024792098,0.12379009954256827,0.12156266553844047,0.11917046652265163,0.11660685446879246,0.11386570897949126,0.11094158681457127,0.10782988729662912,0.10452703349855595,0.10103066857770548,0.09733986588059378,0.09345535043803148,0.08937972812255837,0.08511771694772013,0.0806763726279413,0.07606529744604681,0.07129681754297233,0.06638610882928939,0.06135124580616163,0.05621314093499279,0.050995335698515665,0.04572360041090786,0.04042530343840175,0.03512853409823747,0.02986103765013885,0.024649231380957613,0.01951820970669738,0.014495990709457555,0.009637150074995531,0.00518163208769162,0.0031718129966901995,0.006416557774655943,0.010942108856309205,0.01569321860842868,0.020547868299230103,0.025482850047717488,0.030487605084358813,0.03554903697177443,0.04064909277564217,0.045765586651072915,0.05087380359830608,0.05594808781227131,0.06096315684578438,0.06589508592620102],[0.13533364076035026,0.13404567026708747,0.1326436930967559,0.13112021275375435,0.12946760041581315,0.12767815229191964,0.12574415792378457,0.12365798051314074,0.12141215037415355,0.11899947260404696,0.11641315002642194,0.1136469223790271,0.11069522257561741,0.10755335064925971,0.10421766565592386,0.1006857953471703,0.09695686276397558,0.09303172800102945,0.08891324216543185,0.08460650890707158,0.08011914670313762,0.07546154217652982,0.07064708091576206,0.06569233729463442,0.06061719836496093,0.055444888666140814,0.050201852383729595,0.044917436342828077,0.039623301676054795,0.0343524741055315,0.029137924822489638,0.02401056316282723,0.01899654164634124,0.014113907882838695,0.00936932463213442,0.004761224622460146,0.0007092202027650617,0.004401586658393946,0.008908563811212767,0.01351089318096421,0.01822891403760018,0.02307298436111175,0.028037666597736908,0.03310518248195469,0.038249538028228176,0.043440083405628126,0.048644284934383615,0.05382975260620072,0.05896564467042325,0.06402358215127026],[0.13540872196639403,0.13412690278891348,0.13273139320002494,0.13121468539524855,0.12956913420413257,0.12778701393575934,0.1258605861990498,0.12378217980401117,0.12154428387395737,0.11913965530138844,0.11656144165355915,0.1138033205676776,0.11085965655634976,0.10772567595450312,0.10439766045672241,0.10087315929035573,0.09715121950694522,0.09323263310398155,0.08912019864659874,0.08481899365885755,0.08033665218247468,0.07568363939911579,0.07087351186059505,0.06592314735742387,0.06085292232974368,0.05568680633953602,0.05045233155974939,0.04518037924806803,0.03990470323634588,0.03466108120140491,0.02948594812141833,0.024414329063239763,0.019476875551694996,0.014695913208816674,0.010081048475760303,0.005629513098670117,0.0014593623407890635,0.003275582990677884,0.007627374392722962,0.012151887430813335,0.01684185859729759,0.021696212184360603,0.026699732088033598,0.03182619453808555,0.03704266595040223,0.04231304433392844,0.047600667839229255,0.0528701203970334,0.058088411821165746,0.06322569249069014]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 0.97 (SEM: None)\u003cbr\u003eC: 0.0160084\u003cbr\u003egamma: 85.2516","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0234392\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0272673\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0229824\u003cbr\u003egamma: 690.262","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223817\u003cbr\u003egamma: 631.808","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223928\u003cbr\u003egamma: 633.153"],"visible":true,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],"xaxis":"x","y":[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 0.97 (SEM: None)\u003cbr\u003eC: 0.0160084\u003cbr\u003egamma: 85.2516","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0234392\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0272673\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0229824\u003cbr\u003egamma: 690.262","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223817\u003cbr\u003egamma: 631.808","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.0223928\u003cbr\u003egamma: 633.153"],"visible":true,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],"xaxis":"x2","y":[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],"yaxis":"y2","type":"scatter"}],                        {"annotations":[{"font":{"size":14},"showarrow":false,"text":"Mean","x":0.25,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"font":{"size":14},"showarrow":false,"text":"Standard Error","x":0.8,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"showarrow":false,"text":"x-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.26,"yanchor":"top","yref":"paper"},{"showarrow":false,"text":"y-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.4,"yanchor":"top","yref":"paper"}],"autosize":true,"height":450,"hovermode":"closest","legend":{"orientation":"v","x":0,"y":-0.2,"yanchor":"top"},"margin":{"b":100,"l":35,"pad":0,"r":35,"t":35},"title":{"text":"accuracy"},"updatemenus":[{"buttons":[{"args":[{"x":[[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125]],"y":[[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528]],"z":[[[0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687,0.8667798573550687],[0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303,0.8698797350355303],[0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911,0.873122954183911],[0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357,0.8765114297164357],[0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011,0.8800464350818011],[0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554,0.8837284957847554],[0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298,0.8875572727209298],[0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475,0.8915314350333475],[0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855,0.8956485223734855],[0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989,0.899904796687989],[0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067,0.9042950839741067],[0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081,0.9088126068749081],[0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462,0.9134488095468462],[0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415,0.9181931769605415],[0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884,0.9230330517311884],[0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991,0.9279534527650991],[0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146,0.9329369015086146],[0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343,0.9379632634556343],[0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586,0.9430096148739586],[0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768,0.9480501475073768],[0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368,0.9530561273412368],[0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978,0.9579959273840978],[0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055,0.9628351587369055],[0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823,0.9675369287701823],[0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662,0.9720622595424662],[0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555,0.9763707028094555],[0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298,0.9804211886195298],[0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687,0.9841731401766687],[0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919,0.9875878746771919],[0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651,0.9906302827358651],[0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005,0.9932707301522005],[0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517,0.9954870448727517],[0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729,0.9972663256141729],[0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771,0.998606118337771],[0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376,0.9995142279449376],[1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599,1.0000060680710599],[1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015,1.0000983466320015],[0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121,0.9997999577708121],[0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491,0.9991070165378491],[0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972,0.9980080814056972],[0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153,0.9964933442368153],[0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327,0.9945605598591327],[0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758,0.9922170481869758],[0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354,0.9894793332929354],[0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968,0.9863716854141968],[0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849,0.9829242926104849],[0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069,0.9791714376766069],[0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238,0.9751498586006238],[0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234,0.9708973632319234],[0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684,0.9664517112496684]],[[0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983,0.13537098641802983],[0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026,0.13408935888684026],[0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545,0.13269462431246545],[0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232,0.13117938949612232],[0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695,0.12953613638308695],[0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112,0.12775727895082112],[0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273,0.12583523069953273],[0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956,0.12376248373599956],[0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747,0.12153170043975747],[0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042,0.11913581867234042],[0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163,0.11656817142548163],[0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986,0.11382262169062986],[0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475,0.11089371315319475],[0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596,0.10777683704901596],[0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933,0.1044684151389933],[0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173,0.10096609822344173],[0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252,0.09726897888122252],[0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378,0.09337781611660378],[0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456,0.08929526824682456],[0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619,0.08502612856125619],[0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595,0.08057755590039595],[0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323,0.075959289187323],[0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684,0.07118383092993684],[0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374,0.06626657964772374],[0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286,0.061225884990632286],[0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245,0.056082992161244245],[0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789,0.05086183479467789],[0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149,0.04558862950251149],[0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204,0.040291225154648204],[0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265,0.03499817572232265],[0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473,0.029737561931001473],[0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507,0.024535753034808507],[0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754,0.019416807464575754],[0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092,0.014405067160148092],[0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372,0.009542921911086372],[0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702,0.005018421317446702],[0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108,0.002780389309550108],[0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757,0.006109021022151757],[0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798,0.01065572094086798],[0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142,0.015397893214190142],[0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385,0.020238381072294385],[0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357,0.025161622652995357],[0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132,0.03015951108384132],[0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354,0.03521938204913354],[0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231,0.04032275407798231],[0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835,0.045446672428532835],[0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845,0.05056556635901845],[0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966,0.05565296072324966],[0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992,0.06068284523671992],[0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609,0.06563067772574609]],[],[],[[0.7825999309160263,0.7817688174220705,0.7809595144128343,0.7801754532937346,0.7794200579395778,0.7786967113067211,0.7780087204335573,0.7773592804424426,0.7767514382506865,0.776188056775596,0.775671780472028,0.7752050030641993,0.7747898383216179,0.7744280946787895,0.7741212544091469,0.773870457937605,0.7736764937183724,0.773539793922955,0.773460435987656,0.7734381498715952,0.7734723306869475,0.7735620561935729,0.7737061085095965,0.7739029992844799,0.7741509975154313,0.7744481591624361,0.7747923577297153,0.7751813150277268,0.7756126314039138,0.7760838148252795,0.77659230830422,0.7771355152738038,0.7777108226335012,0.7783156212958525,0.7789473241645226,0.7796033815616199,0.7802812941951828,0.7809786238155454,0.7816930017519327,0.7824221355488601,0.783163813937008,0.7839159103768798,0.7846763854075882,0.7854432880195352,0.7862147562504994,0.7869890171815688,0.7877643864841568,0.788539267643465,0.7893121509584601,0.7900816123946789],[0.7791559637444286,0.7782057241461113,0.7772791216893056,0.7763802104585884,0.7755130538820211,0.7746816836386519,0.7738900559887403,0.7731420062952051,0.7724412026589015,0.771791099724937,0.7711948938205637,0.7706554806455965,0.7701754167436399,0.7697568859293007,0.7694016717297552,0.7691111367203927,0.7688862094011508,0.7687273789852981,0.7686346981728372,0.7686077936761178,0.7686458839760484,0.7687478035323339,0.7689120324658518,0.7691367305861854,0.7694197745574396,0.7697587969802443,0.7701512262118976,0.7705943258407871,0.7710852328640725,0.7716209937765963,0.7721985979518557,0.7728150078714293,0.7734671859281248,0.774152117682944,0.7748668315915583,0.7756084153291507,0.776374028931811,0.7771609150382196,0.7779664065583529,0.7787879321184518,0.7796230196361609,0.78046929836954,0.7813244997616682,0.7821864573718875,0.7830531061482561,0.7839224812561508,0.7847927166374906,0.7856620434356669,0.7865287883845107,0.7873913722266282],[0.7755612046875043,0.7744806447697367,0.7734253528728785,0.7724000881223575,0.7714096452466597,0.7704588045834847,0.7695522780635919,0.7686946520978671,0.7678903285405567,0.7671434651319713,0.7664579170171881,0.7658371810720691,0.7652843448237983,0.7648020417135061,0.7643924143033781,0.7640570867792117,0.7637971477516852,0.7636131439364642,0.7635050848246184,0.7634724579763992,0.7635142541204066,0.7636290008505229,0.763814803411347,0.7640693908659104,0.7643901658526633,0.7647742561572345,0.7652185664348329,0.7657198286022541,0.7662746496523576,0.7668795559065364,0.767531032992014,0.7682255610939053,0.7689596452739409,0.7697298408595719,0.7705327740835405,0.771365158292682,0.7722238061459894,0.7731056382879375,0.7740076890171372,0.7749271094768218,0.7758611688771431,0.7768072542246098,0.7777628689859861,0.7787256310570887,0.7796932703452455,0.7806636262113273,0.7816346449562337,0.7826043774799445,0.7835709771905172,0.7845326981969258],[0.7718623059270656,0.7706410612165414,0.7694463935628939,0.7682838457596898,0.767159035034543,0.7660775932193596,0.7650451007920248,0.7640670158288773,0.763148599295066,0.7622948384859423,0.761510370784614,0.7607994101803887,0.7601656791596841,0.7596123485981022,0.7591419881227505,0.7587565290671752,0.7584572416184727,0.7582447270913604,0.7581189255115965,0.7580791379188812,0.7581240620783276,0.758251839683534,0.7584601126904693,0.7587460861651657,0.7591065949618925,0.7595381716542602,0.7600371133873698,0.7605995456647621,0.7612214814882771,0.7618988746942609,0.7626276667446884,0.7634038266134441,0.7642233837407978,0.7650824543045077,0.7659772612710614,0.7669041488465193,0.7678595920473313,0.7688402021632379,0.7698427288938092,0.7708640599146862,0.7719012185765144,0.7729513603661075,0.7740117686722617,0.7750798503040603,0.7761531311129334,0.7772292519758623,0.7783059653097435,0.7793811322089437,0.7804527202314758,0.7815188018050608],[0.7681194613695492,0.766748773735469,0.7654055076275009,0.7640960556586267,0.7628269397237039,0.7616047410584158,0.7604360212146433,0.7593272349707856,0.7582846367789403,0.7573141829775872,0.7564214326209984,0.7556114503302318,0.754888714977716,0.75425703819749,0.7537194965968279,0.7532783810912964,0.7529351659967157,0.7526904994421109,0.7525442154201747,0.7524953665017597,0.7525422750528251,0.7526825998320117,0.7529134142003125,0.7532312918756201,0.7536323961988919,0.7541125691913464,0.7546674171973562,0.7552923905435667,0.7559828553262368,0.7567341561054826,0.7575416688941157,0.7584008443538468,0.7593072415404207,0.7602565528695979,0.761244621212496,0.7622674501803551,0.7633212087359573,0.7644022312831171,0.76550701434812,0.7666322108886326,0.7677746231566762,0.7689311949123906,0.7700990036433933,0.7712752532986378,0.7724572679028978,0.7736424862843708,0.7748284580281202,0.7760128406656008,0.7771933980273302,0.7783679996226198],[0.7644066131624461,0.7628803037087047,0.7613816503171235,0.7599179368033685,0.7584966500663786,0.7571254009998493,0.7558118324120877,0.7545635146595495,0.7533878305168161,0.7522918517687283,0.7512822110645343,0.7503649736232054,0.7495455142848727,0.7488284059961017,0.7482173259238347,0.7477149848811532,0.7473230845710898,0.7470423053876852,0.7468723253575404,0.7468118685525154,0.7468587792714871,0.7470101167412799,0.7472622641805664,0.7476110458334412,0.7480518459277447,0.7485797242935467,0.7491895244132124,0.7498759708047873,0.7506337537401615,0.7514576002865521,0.7523423314908446,0.7532829061872415,0.7542744524046622,0.7553122876972169,0.7563919299389131,0.7575091002331482,0.7586597196075445,0.7598399011122763,0.7610459388301378,0.7622742951526504,0.7635215874908454,0.764784575383674,0.7660601487523825,0.7673453178360211,0.7686372051409045,0.7699330395532767,0.7712301526058247,0.772525976759172,0.7738180454610394,0.7751039946782909],[0.7608104380917559,0.7591260543073426,0.7574688295023149,0.7558469400227967,0.7542688589464538,0.7527432707000669,0.7512789679898937,0.7498847309337657,0.7485691892892454,0.7473406700088852,0.7462070340040997,0.7451755078668066,0.7442525181773246,0.7434435375932246,0.7427529527558381,0.7421839637650132,0.7417385233062466,0.741417320511525,0.7412198107012041,0.7411442879791892,0.7411879940064197,0.7413472537614713,0.7416176279844857,0.7419940722129353,0.7424710935286964,0.7430428979247321,0.743703523179915,0.7444469540201935,0.745267217979871,0.7461584616927069,0.7471150083387711,0.7481313976845871,0.7492024106291635,0.7503230804548164,0.7514886931201405,0.7526947789552756,0.7539370980509242,0.755211621490478,0.7565145103734776,0.7578420943311078,0.7591908509530387,0.76055738724286,0.761938423910599,0.7633307830095909,0.7647313791448358,0.7661372142326659,0.7675453755860294,0.7689530369414197,0.7703574619341902,0.7717560094669115],[0.7574276161041409,0.7555876707133791,0.7537735987160631,0.7519944149052549,0.7502595407713224,0.7485787178578799,0.746961898641737,0.7454191133693945,0.7439603122344476,0.7425951837986042,0.7413329527716008,0.7401821632167636,0.7391504567926845,0.738244359311351,0.7374690918284916,0.7368284235318137,0.736324581801008,0.7359582296125362,0.7357285127358465,0.7356331707551761,0.7356686990016452,0.7358305444995439,0.7361133183508335,0.7365110089109779,0.7370171834948664,0.7376251701232277,0.738328214265178,0.7391196083186486,0.7399927936365682,0.7409414363374398,0.7419594790704205,0.7430411714714629,0.7441810823579932,0.745374096844274,0.7466154015700893,0.7479004611526472,0.7492249888121361,0.750584913893493,0.7519763487160073,0.753395556834933,0.7548389244057198,0.7563029359171816,0.7577841551248499,0.7592792115925715,0.7607847928618755,0.762297641934694,0.7638145594903587,0.765332410070276,0.766848131353997,0.7683587456127995],[0.7543599151104028,0.7523730363067228,0.7504100163101179,0.7484805901925393,0.7465950156751773,0.7447639914999795,0.7429985497212734,0.7413099184986991,0.7397093524137892,0.7382079284193244,0.7368163076381854,0.7355444668201967,0.7344014087484856,0.7333948682393471,0.7325310385199496,0.7318143489843507,0.7312473256446319,0.7308305569209714,0.7305627706231158,0.7304410088064978,0.730460872971041,0.7306168069102793,0.7309023875185457,0.7313106012504538,0.7318340920473634,0.732465373327446,0.7331970014774369,0.7340217113876442,0.7349325163972008,0.735922776004162,0.7369862351764023,0.7381170392946064,0.7393097288012118,0.7405592175908389,0.7418607590894344,0.7432099038357081,0.7446024521890845,0.7460344055269146,0.7475019189455415,0.7490012580387515,0.7505287617998284,0.7520808131011358,0.7536538175821381,0.7552441911655114,0.7568483558652506,0.7584627430883367,0.7600838032886503,0.7617080206195985,0.7633319311466593,0.7649521432068045],[0.7517068599663337,0.7495885447199085,0.747491562326079,0.7454261935464632,0.7434033468653115,0.7414344866001118,0.7395315336205396,0.7377067338197311,0.7359724891237196,0.7343411457878442,0.7328247354148032,0.7314346663197101,0.7301813679668867,0.7290739013124299,0.7281195648602021,0.7273235481923356,0.7266887006006664,0.726215473397984,0.7259020527307762,0.7257446468399533,0.725737861213752,0.7258750973462416,0.726148930941245,0.7265514462246501,0.7270745173970111,0.7277100362914873,0.7284500891907036,0.72928708737773,0.7302138565051088,0.7312236898837883,0.732310370636023,0.7334681674746762,0.7346918087309897,0.7359764391697865,0.737317564089945,0.7387109851719915,0.7401527324528983,0.741638996624534,0.7431660655165551,0.7447302681053249,0.7463279286859508,0.7479553329886147,0.7496087070800916,0.7512842089552667,0.7529779318839265,0.754685917912072,0.7564041794720038,0.7581287268435511,0.7598555992098771,0.7615808972223315],[0.7495563141810011,0.7473288699752499,0.7451200869541632,0.7429405890942544,0.740801704882911,0.7387154052177227,0.7366942144222999,0.7347510890882276,0.7328992586570869,0.7311520207993347,0.7295224837998416,0.7280232475536397,0.7266660151460729,0.7254611307120157,0.7244170535895869,0.723539820629852,0.7228326292138485,0.7222957233063412,0.7219266484102115,0.7217207439684687,0.7216716951828559,0.7217720438276733,0.7220136255370321,0.7223879301396924,0.7228863906219726,0.723500608314998,0.7242225218039007,0.7250445263951817,0.7259595502472732,0.7269610926351477,0.7280432293444923,0.7292005898980767,0.7304283112101804,0.7317219723295187,0.7330775151293466,0.7344911560692037,0.7359592943899462,0.7374784221928412,0.7390450416707951,0.7406555942075159,0.742306405101758,0.7439936463586914,0.7457133184579299,0.7474612504581741,0.7492331164423955,0.7510244653109548,0.7528307603768378,0.7546474251010298,0.7564698915496109,0.7582936486426467],[0.747974219912496,0.7456655163500318,0.7433730650724641,0.7411076379684215,0.7388807506077413,0.7367046055733699,0.7345920095373416,0.7325562588272618,0.7306109873978236,0.7287699701728293,0.7270468736416942,0.725454944363507,0.7240066246332937,0.7227130829853602,0.7215836455099796,0.7206251145690216,0.7198410382504384,0.719231441311991,0.7187933705721405,0.7185216474190668,0.7184095190833458,0.7184491989329274,0.7186323095807811,0.7189502413056692,0.7193944365616058,0.7199566098010327,0.7206289104807262,0.7214040359558438,0.7222752999987357,0.7232366619153794,0.7242827206918409,0.7254086783107898,0.7266102763599083,0.7278837103273943,0.7292255265359889,0.7306325074478213,0.7321015519452199,0.733629557937153,0.7352133149671535,0.7368494141124239,0.7385341811767622,0.7402636370217268,0.7420334861481641,0.7438391318323618,0.7456757137704504,0.7475381626732072,0.749421265705318,0.7513197369571906,0.753228288005559,0.7551416947637029],[0.7469957312615803,0.7446366951195749,0.7422920340495838,0.7399724915571565,0.7376895554273006,0.735455400786928,0.7332828068537118,0.7311850421143571,0.7291757118442225,0.7272685609331542,0.7254772239063171,0.7238149128150924,0.7222940323392208,0.7209257101642216,0.7197192308903195,0.7186813765114043,0.7178157921549626,0.7171227815504044,0.7165997469854284,0.7162418826219774,0.7160428197935041,0.7159951706680261,0.7160909760965715,0.7163220689513383,0.7166803634159817,0.71715807924842,0.7177479086441045,0.718443132079049,0.71923768842822,0.720126203753527,0.7211039824661523,0.7221669641387749,0.7233116491452837,0.7245349966294133,0.7258342991432319,0.7272070397066892,0.7286507389594797,0.7301628022234046,0.7317403780803149,0.7333802406556219,0.7350787063712341,0.7368315922053015,0.7386342170861262,0.7404814423724627,0.7423677429943558,0.7442872986890158,0.7462340948673111,0.7482020243037997,0.7501849831832239,0.7521769573708972],[0.7466203397397345,0.7442416681991937,0.7418760145764876,0.7395339190591206,0.7372266285877334,0.7349660341015262,0.7327645808253722,0.7306351463761962,0.7285908807444621,0.7266450015025787,0.724810537073267,0.7231000110047973,0.7215250621318439,0.7200960022707911,0.7188213313600811,0.7177072688577827,0.7167574137796788,0.7159726604809968,0.7153514119702302,0.7148900052241217,0.7145832163695426,0.7144247519680756,0.7144076839085142,0.7145248157677198,0.7147689813309264,0.715133280261987,0.7156112567964344,0.7161970269551378,0.7168853589802568,0.717671710806031,0.7185522275413166,0.7195237012543076,0.7205834949181383,0.7217294323549104,0.7229596566435952,0.7242724610666542,0.7256660996244535,0.7271385885985695,0.7286875160271534,0.7303098803769766,0.7320019800336999,0.7337593688967021,0.7355768811235786,0.7374487147819163,0.7393685555068975,0.7413297195518489,0.7433252991436452,0.7453482985848665,0.7473917546813852,0.7494488388486188],[0.7468126714486056,0.7444416533024928,0.7420825457501081,0.73974550029158,0.7374413031707475,0.7351813035041613,0.7329773144017402,0.7308414825955586,0.7287861219752586,0.7268235067686334,0.724965621348992,0.7232238665578342,0.7216087281505056,0.7201294228005082,0.7187935513554623,0.7176068046213292,0.7165727751444693,0.7156929181335198,0.7149666734453085,0.7143917226317049,0.7139643307575013,0.7136797202203607,0.7135324360049947,0.7135166775004924,0.713626584616282,0.7138564739580942,0.71420102516692,0.7146554194899356,0.7152154332489389,0.7158774887303316,0.716638664505189,0.7174966665079388,0.7184497604967012,0.7194966659245615,0.7206364109854689,0.7218681490914478,0.7231909391653553,0.72460349748733,0.7261039394508986,0.727689545417229,0.729356597986257,0.7311003316944996,0.7329150030863465,0.7347940504431836,0.7367302963703903,0.7387161549107301,0.7407438213596533,0.7428054358473062,0.7448932189604307,0.7469995809887116],[0.7475086852942592,0.7451669430196806,0.7428358844870916,0.7405250963860339,0.7382447067783267,0.7360053057962123,0.733817841419814,0.7316934875149543,0.7296434819655466,0.7276789340457424,0.7258106024466237,0.724048648910007,0.7224023773884911,0.7208799747547893,0.7194882751875131,0.7182325742864999,0.7171165180182123,0.7161420840449892,0.7153096598540171,0.7146182073604508,0.71406549223842,0.7136483511381083,0.7133629710243485,0.7132051598185378,0.713170593706691,0.7132550320868261,0.7134544953852742,0.7137654037913111,0.7141846765821793,0.714709792450197,0.7153388113757063,0.7160703583195157,0.7169035684768745,0.7178379931355117,0.7188734643829036,0.7200099161002799,0.721247158091784,0.722584600700584,0.7240209325433127,0.725553777369868,0.7271794187601127,0.7288927314902306,0.730687352263666,0.7325559683602529,0.7344906104772896,0.7364829082667943,0.738524302677656,0.7406062186588167,0.7427202034421034,0.7448580354736687],[0.7486252557996147,0.7463277306089853,0.7440392334487727,0.7417686525495205,0.739525321537402,0.7373189383258266,0.7351594631940086,0.7330569950196087,0.7310216256468511,0.7290632738837797,0.7271915027008187,0.7254153258236159,0.723743012880482,0.7221819051351508,0.7207382559027572,0.7194171101626731,0.718222235951725,0.7171561156929842,0.7162199993375231,0.715414014413275,0.714737322329758,0.7141883067059971,0.7137647784118154,0.7134641830422105,0.7132837988836868,0.713220916257011,0.7132729918159961,0.7134377735983802,0.7137133942368217,0.7140984307598813,0.7145919299261917,0.7151933981397531,0.7159027547827235,0.7167202473483434,0.7176463261148508,0.7186814753075799,0.7198259967724101,0.7210797411394538,0.7224417802927116,0.7239100137273641,0.7254807382700285,0.727148532547083,0.7289066035312988,0.7307471709412408,0.7326617872740018,0.7346416015006918,0.7366775746534461,0.7387606544448824,0.740881915104877,0.7430326677807746],[0.7500706052314632,0.7478256201632305,0.7455873981971812,0.7433640571836306,0.7411640773395527,0.7389962245134446,0.7368694574558137,0.734792819306773,0.7327753144786637,0.7308257733437789,0.7289527085977877,0.7271641687534522,0.725467595737228,0.7238696947411745,0.7223763250046203,0.7209924197726812,0.7197219421421587,0.7185678809254086,0.7175322873646202,0.7166163500360552,0.7158205021734338,0.7151445533745762,0.714587836465479,0.7141493601538226,0.7138279587863889,0.7136224317165725,0.7135316661775536,0.7135547388969072,0.7136909928186945,0.7139400861378487,0.7143020113761707,0.7147770824533282,0.7153658876621202,0.7160692061842551,0.7168878853245076,0.7178226750588653,0.7188740159386849,0.7200417764723411,0.7213249397721839,0.7227212600712614,0.7242269794405968,0.7258367671962878,0.7275439222606728,0.7293406919053469,0.7312185838730267,0.7331686353071081,0.7351816361774698,0.7372483120299916,0.739359471671267,0.7415061249732826],[0.7517536646052168,0.7495636863972572,0.7473775334997825,0.7452025412987742,0.7430463456775569,0.7409168151452203,0.7388219713672922,0.7367698989214728,0.7347686458479898,0.7328261174172697,0.7309499664421384,0.7291474843299143,0.7274254977831653,0.7257902764794464,0.724247457057563,0.7228019882153365,0.7214581006564873,0.7202193040801752,0.7190884115472521,0.718067589609653,0.71715843079808,0.7163620436352685,0.7156791544051346,0.715110214492678,0.7146555071591668,0.7143152480163847,0.7140896740725542,0.7139791169062789,0.7139840561737503,0.7141051501926661,0.7143432407332069,0.7146993293753982,0.7151745228933918,0.7157699451836481,0.7164866134501978,0.7173252771014095,0.7182862199784548,0.7193690318733377,0.7205723664354664,0.7218937205415055,0.7233292870295366,0.7248739277608726,0.7265212761092844,0.7282639329971853,0.730093703803803,0.7320018353736137,0.733979231583167,0.7360166395952876,0.7381048059619774,0.740234604705321],[0.7535914354864253,0.7514541816881776,0.7493171500711819,0.7471869261091234,0.7450703568789949,0.7429744944103815,0.7409065309045615,0.7388737268076153,0.736883333237745,0.7349425108081392,0.733058247409625,0.7312372779658103,0.7294860094828601,0.7278104548218199,0.7262161784702268,0.7247082571524692,0.7232912574006177,0.7219692312548763,0.720745730157733,0.719623835955366,0.7186062068371426,0.7176951351284324,0.7168926131723987,0.7162004031225606,0.7156201063106099,0.7151532279130458,0.7148012328571626,0.7145655892185216,0.7144477957125723,0.7144493902346623,0.7145719367440397,0.7148169881442454,0.7151860232616726,0.7156803567176061,0.7163010216826218,0.7170486275767927,0.7179231981948646,0.7189240007935026,0.7200493829393197,0.7212966394039195,0.7226619324802698,0.7241402824975907,0.7257256316763621,0.7274109695467171,0.7291884987431457,0.7310498186444802,0.7329861087364368,0.7349882998652204,0.737047227094847,0.7391537617769302],[0.7555142097804044,0.7534238687920276,0.7513295169961522,0.7492370481104621,0.7471525995656207,0.7450825077968906,0.7430332578948619,0.74101142851141,0.739023633249452,0.7370764600894122,0.7351764106931107,0.7333298416445684,0.731542909803643,0.7298215239327298,0.728171304588109,0.7265975539386906,0.7251052366958521,0.7236989727367603,0.7223830413236132,0.7211613961163909,0.7200376895032394,0.7190153041812277,0.7180973894491387,0.7172868993448426,0.7165866295770551,0.7159992501547723,0.715527330687838,0.7151733554969393,0.7149397259136911,0.7148287474667183,0.7148426000528529,0.7149832897253199,0.715252581465939,0.7156519133490858,0.7161822939699239,0.7168441869893439,0.717637389121711,0.7185609105992381,0.7196128694771431,0.7207904121593216,0.722089671274218,0.723505768130534,0.7250328611087066,0.7266642351377114,0.7283924226823452,0.7302093444850369,0.7321064586143109,0.7340749083380265,0.7361056619622215,0.7381896403084234],[0.75746892099905,0.7554173697378341,0.7533569812376082,0.7512930240240252,0.7492310098750778,0.7471766608316394,0.7451358722392035,0.7431146725161654,0.74111918054573,0.7391555617725846,0.7372299842347875,0.7353485758581464,0.7335173843680143,0.7317423411186508,0.730029229995441,0.7283836623102236,0.7268110582932558,0.725316635403948,0.7239054032605459,0.7225821645550872,0.7213515209040746,0.7202178822149996,0.7191854778465383,0.7182583676213483,0.7174404506229797,0.7167354696742617,0.7161470094516911,0.7156784863363643,0.7153331283376744,0.7151139437588925,0.7150236777204779,0.7150647562434882,0.7152392183532227,0.7155486376193738,0.7159940357079516,0.7165757918372635,0.7172935533807326,0.7181461540193474,0.7191315465065728,0.72024675694322,0.7214878662527816,0.7228500223267719,0.724327483410333,0.7259136902915782,0.7276013623538801,0.729382610979875,0.7312490632897692,0.7331919896049854,0.7352024290424396,0.7372713089330125],[0.7594210280946845,0.7573990108365758,0.7553627638079987,0.7533169920420201,0.7512666568906263,0.7492169541505926,0.7471732892941103,0.7451412502620245,0.7431265783898273,0.7411351381315858,0.7391728863151841,0.7372458416945555,0.7353600555530589,0.7335215840515075,0.7317364629025616,0.7300106847924324,0.728350179767679,0.72676079857008,0.7252482986502689,0.7238183323373502,0.7224764364039519,0.7212280220601017,0.7200783642487208,0.7190325890110922,0.7180956576499598,0.7172723464456701,0.7165672207800762,0.7159846026963219,0.7155285311735591,0.7152027147289485,0.7150104763809969,0.7149546915233764,0.7150377198666178,0.7152613332941948,0.7156266422168539,0.7161340237333729,0.7167830555237655,0.7175724597920548,0.7185000616126926,0.7195627656163448,0.7207565540420527,0.7220765078452811,0.723516850947417,0.7250710160735042,0.7267317291935966,0.7284911085484662,0.7303407736965601,0.7322719599570168,0.7342756339547651,0.7363426065694386],[0.7613552993573088,0.7593535729232832,0.7573316794519315,0.7552938080866469,0.7532444271897942,0.7511882729709662,0.7491303359050786,0.7470758451608153,0.7450302513103633,0.7429992076282554,0.7409885503057934,0.739004277903876,0.7370525303381545,0.7351395676350103,0.7332717486156519,0.7314555095617049,0.7296973427944126,0.7280037749683732,0.726381344748715,0.7248365794176386,0.7233759698525475,0.7220059432429421,0.7207328328751887,0.7195628443196622,0.7185020174082984,0.7175561834951572,0.716730917649567,0.7160314856409977,0.7154627858361469,0.7150292864397431,0.7147349588671636,0.7145832084314321,0.7145768039460458,0.7147178082666634,0.7150075121867008,0.7154463744211987,0.7160339706080171,0.7167689542713604,0.7176490324838636,0.718670958505215,0.7198305429759274,0.7211226843522858,0.7225414182671299,0.72407998449854,0.7257309093348475,0.7274861004307147,0.7293369508110835,0.7312744485119007,0.7332892884256006,0.7353719831961862],[0.7632757633819205,0.7612862289302748,0.7592700727381767,0.7572309957643834,0.7551730075155945,0.7531004247544766,0.751017868476058,0.7489302591520908,0.7468428102477036,0.7447610200099605,0.7426906615121553,0.7406377709099592,0.7386086338259187,0.7366097697284899,0.7346479141132644,0.7327299982311284,0.7308631260457801,0.7290545480473428,0.7273116315063006,0.7256418267294421,0.7240526288832559,0.7225515349858184,0.7211459957398352,0.7198433619896973,0.7186508257348807,0.7175753558195522,0.7166236286406872,0.7158019544693688,0.7151162002554601,0.7145717100757252,0.7141732246789193,0.7139248018648487,0.7138297396915927,0.71389050471633,0.714108667618062,0.7144848486008457,0.7150186749105222,0.715708752597394,0.7165526543117824,0.7175469244321454,0.7186871022161909,0.7199677629707995,0.7213825765072146,0.722924381442182,0.7245852732812,0.7263567037252023,0.7282295883093426,0.73019441932531,0.732241380991052,0.7343604639927903],[0.7652049795279001,0.7632218195174099,0.7612051162986448,0.759158087437542,0.7570842915340767,0.7549876368435512,0.7528723885917981,0.7507431747869953,0.7486049902977724,0.7464631989276853,0.7443235331704976,0.7421920912803088,0.7400753312375613,0.7379800611394304,0.7359134254951245,0.7338828868680425,0.7318962022831508,0.729961393815294,0.728086712798387,0.7262805971520885,0.7245516214162021,0.7229084392168827,0.7213597180640064,0.7199140665948763,0.7185799546322724,0.717365626708586,0.7162790100136729,0.7153276180408267,0.7145184515195346,0.7138578985201917,0.7133516358782782,0.7130045342965086,0.7128205696260902,0.7128027428864612,0.7129530115427064,0.7132722344107698,0.7137601322970271,0.7144152661017504,0.7152350336344571,0.7162156858208399,0.7173523623523599,0.7186391461744683,0.720069135566291,0.7216345319730519,0.7233267412489589,0.7251364855820149,0.7270539231224507,0.7290687722306295,0.7311704372942444,0.7333481332240952],[0.7671826764332843,0.7652035030930325,0.7631834930538983,0.761125361772431,0.7590321979995924,0.7569074823650737,0.7547551051575438,0.7525793829370463,0.7503850735473262,0.7481773890216811,0.7459620057979892,0.7437450715797658,0.7415332081042583,0.7393335090106036,0.7371535319466597,0.735001284018858,0.732885199682425,0.7308141101968324,0.7287972038403667,0.7268439761944646,0.7249641699776,0.7231677041327049,0.7214645921511617,0.7198648499469312,0.7183783939690861,0.7170149306488119,0.7157838387025941,0.714694046238135,0.7137539050118211,0.7129710645427384,0.712352349074133,0.7119036405658039,0.7116297709798483,0.7115344270718283,0.7116200707104051,0.7118878774190287,0.7123376953703939,0.7129680264838638,0.7137760306024636,0.7147575529911728,0.7159071746393529,0.717218284107274,0.7186831689695237,0.7202931243127497,0.7220385752713191,0.7239092102528869,0.7258941213271052,0.7279819482246691,0.7301610225108148,0.7324195087390625],[0.7692637245376436,0.7672907266664842,0.765269387622809,0.763201880368893,0.7610907794776937,0.758939089817195,0.7567502751164785,0.7545282859231277,0.7522775863570635,0.7500031789537529,0.7477106267727611,0.7454060718298653,0.7430962487976509,0.7407884928172211,0.738490740180098,0.7362115205835282,0.7339599396438807,0.7317456503818295,0.7295788124795248,0.7274700382630978,0.725430324590972,0.7234709701341953,0.7216034779201962,0.7198394434720518,0.7181904294019478,0.7166678278941497,0.7152827131172741,0.7140456862095889,0.7129667160512441,0.7120549795370115,0.711318705454856,0.7107650263239229,0.7103998426201419,0.7102277036969944,0.710251709382927,0.7104734357087625,0.7108928875061555,0.7115084797536224,0.7123170485740323,0.7133138917597954,0.7144928376770809,0.7158463404359492,0.7173655983619639,0.7190406921102654,0.7208607382563426,0.7228140538956925,0.7248883276894784,0.7270707928937786,0.7293483981833834,0.7317079724961711],[0.7715153524830306,0.7695564020874534,0.7675416443192519,0.7654726522397456,0.763351420723086,0.7611804052569546,0.7589625615753953,0.7567013855612352,0.7544009527141354,0.7520659563260148,0.7497017433414447,0.7473143467110946,0.7449105128775609,0.7424977228728754,0.7400842053654975,0.7376789398833659,0.7352916483719563,0.7329327732369577,0.7306134400854091,0.7283454035320165,0.7261409746924467,0.7240129293533596,0.7219743962957721,0.7200387258535061,0.7182193395032908,0.7165295620888572,0.714982439148848,0.7135905427072612,0.712365769745358,0.7113191383478965,0.710460587142826,0.7097987840722193,0.7093409506905474,0.7090927080453072,0.7090579497346783,0.7092387469611434,0.7096352893382631,0.7102458639144388,0.7110668734279496,0.7120928932919566,0.7133167653228165,0.7147297248633162,0.7163215567957214,0.7180807750503266,0.7199948196321042,0.722050264924176,0.7242330330709507,0.7265286065636182,0.7289222346987483,0.7313991292996824],[0.7740134926568263,0.7720831428264381,0.7700899142017588,0.7680347135683143,0.7659188770690442,0.7637442187436242,0.7615130811568085,0.7592283875549642,0.7568936948137892,0.7545132462424344,0.7520920230921426,0.7496357933848928,0.7471511564354905,0.7446455811974738,0.7421274363304746,0.7396060096785906,0.7370915146834053,0.7345950811519896,0.7321287277825002,0.7297053139423783,0.7273384684212735,0.7250424932654423,0.722832241360588,0.7207229671764468,0.718730151018053,0.7168692982300514,0.7151557160384321,0.7136042720357348,0.7122291396484697,0.7110435371791739,0.7100594680880297,0.7092874709643324,0.7087363880374402,0.7084131610107866,0.708322662423305,0.7084675696443253,0.7088482870322033,0.7094629198227397,0.7103073010908221,0.71137507080591,0.7126578037482676,0.7141451810299126,0.7158251983084309,0.7176844025903729,0.7197081488446524,0.7218808674876122,0.7241863341198174,0.7266079336156986,0.7291289116949106,0.7317326083333098],[0.776838154665799,0.77495842692495,0.7730096198083531,0.770991910534398,0.7689058960039585,0.7667526499961378,0.7645337839990144,0.7622515112107856,0.7599087130442886,0.7575090072324314,0.7550568163635698,0.7525574353760167,0.7500170962138505,0.747443027499101,0.7448435067192231,0.7422279020789718,0.739606700842931,0.7369915207252873,0.7343951006987843,0.7318312675323321,0.7293148744675026,0.7268617087509497,0.7244883652936492,0.7222120845631301,0.7200505539532099,0.7180216733189368,0.7161432870870635,0.714432887295295,0.7129072939796683,0.7115823213833473,0.7104724403338201,0.7095904486402569,0.708947162308595,0.7085511405917421,0.7084084572690901,0.7085225290406449,0.7088940095749974,0.7095207547112015,0.7103978608114632,0.7115177745829107,0.7128704691446096,0.7144436780047874,0.716223176172584,0.7181930960157905,0.7203362647527369,0.7226345506013994,0.7250692054925396,0.7276211937228896,0.7302714977886074,0.7330013947063527],[0.7800677853777304,0.7782686121491351,0.7763956256589524,0.7744482296092119,0.7724262166004576,0.770329831905836,0.7681598426149295,0.7659176118875843,0.7636051778472868,0.7612253363875392,0.7587817268595053,0.7562789192525063,0.7537225010705143,0.7511191616504935,0.7484767711693475,0.7458044510582855,0.7431126320064858,0.7404130952188904,0.7377189921345586,0.7350448374621689,0.7324064702089081,0.7298209774388104,0.7273065758737447,0.724882447222308,0.7225685243580051,0.7203852272167188,0.7183531495571849,0.7164927004875431,0.7148237077989898,0.7133649934794322,0.7121339350422816,0.7111460291689634,0.7104144762635891,0.7099498055008973,0.7097595595304287,0.709848056027815,0.7102162397840386,0.7108616342229005,0.7117783955505524,0.7129574667187539,0.7143868226290053,0.7160517930811954,0.7179354463156485,0.7200190138664361,0.7222823368880563,0.7247043150029119,0.7272633407693136,0.7299377057353309,0.732705967350152,0.7355472694101116],[0.7837726879291717,0.7820918501154139,0.7803346290300396,0.7784996500409744,0.7765858733243233,0.774592660961951,0.7725198511317977,0.770367839441171,0.7681376672621365,0.765831116681925,0.7634508113714482,0.761000322293318,0.7584842767099311,0.7559084684070565,0.7532799664174222,0.7506072188160634,0.7479001473767894,0.7451702280502202,0.7424305513860255,0.739695856230854,0.7369825293656692,0.7343085633016343,0.7316934643552686,0.7291581035132189,0.7267245036264484,0.7244155582878263,0.722254680459258,0.7202653825729523,0.7184707943809651,0.7168931300705182,0.715553121732638,0.71446944162716,0.713658140146068,0.7131321291962347,0.7129007412218593,0.7129693917995256,0.7133393685530862,0.7140077613830618,0.7149675394581008,0.7162077701775893,0.7177139656223556,0.7194685340023455,0.7214513081164594,0.7236401202574556,0.7260113932674965,0.7285407201447414,0.7312034090463894,0.7339749759716545,0.7368315731289669,0.7397503464203685],[0.7880077426270202,0.7864901333330618,0.7848964890502776,0.7832247123209598,0.7814729638064697,0.779639728325821,0.7777238894032317,0.7757248127568727,0.773642439023616,0.7714773858195227,0.7692310589698841,0.766905772391219,0.7645048756549366,0.7620328876923695,0.7594956343985753,0.7569003870458105,0.7542559974210606,0.7515730244598302,0.7488638458806025,0.7461427469733846,0.7434259773345948,0.7407317650813697,0.7380802770805751,0.7354935132031767,0.7329951228264844,0.7306101330578771,0.7283645807579398,0.726285044673133,0.7243980800082789,0.7227295655256591,0.7213039823827266,0.7201436536467636,0.7192679825655396,0.7186927347127787,0.7184294124556108,0.718484768465263,0.7188604975520159,0.7195531333055903,0.7205541593301179,0.7218503266339458,0.7234241516961335,0.7252545563383876,0.7273176024124812,0.7295872719916038,0.7320362466930151,0.7346366466686324,0.7373606990524743,0.7401813156692304,0.7430725693152649,0.7460100660749613],[0.7928048920912666,0.7915009575264312,0.7901249913581903,0.7886743077296253,0.7871463843077035,0.7855389221454792,0.7838499148193727,0.7820777276590412,0.7802211878345604,0.7782796859635607,0.7762532897338572,0.7741428697856906,0.7719502377390981,0.7696782957594386,0.7673311963978005,0.7649145105907315,0.7624354006233418,0.7599027935228803,0.7573275487377575,0.7547226120693215,0.7521031456912528,0.7494866217921579,0.7468928650567478,0.7443440270971414,0.7418644744096146,0.7394805709448439,0.7372203375492596,0.735112974058054,0.7331882363858759,0.7314756710794219,0.7300037235418235,0.7287987528399332,0.7278840039616434,0.7272786047723423,0.7269966660444875,0.7270465650393876,0.7274304835624168,0.7281442499116119,0.7291775034601622,0.7305141661807065,0.732133173827823,0.7340093964938972,0.7361146671042437,0.7384188372961377,0.7408907906513005,0.7434993596843221,0.7462141114939607,0.7490059845001005,0.7518477732948575,0.7547144695006297],[0.7981660958539885,0.7971293661524433,0.796028876718947,0.7948615767700359,0.7936244756470223,0.7923146914265545,0.7909295086248411,0.7894664461061487,0.7879233363523127,0.7862984172666435,0.7845904376583065,0.7827987774626655,0.780923583574284,0.7789659218703349,0.7769279455432166,0.7748130791935147,0.7726262172003204,0.7703739336196022,0.7680646991920692,0.7657090989004705,0.7633200408461567,0.760912943991397,0.7585058885735674,0.7561197088787799,0.7537780038637628,0.7515070373628331,0.749335497142196,0.7472940820585373,0.7454148905935238,0.7437305938442484,0.7422733932804059,0.7410737890227238,0.7401592169881488,0.7395526489650034,0.7392712809994011,0.7393254522837436,0.7397179294154232,0.7404436549484941,0.741489999139038,0.7428374833958152,0.7444608812342928,0.7463305624365106,0.7484139348959409,0.7506768530598162,0.7530848927342728,0.7556044288039024,0.7582034868879576,0.7608523674043424,0.7635240594198198,0.7661944726213357],[0.8040576776983853,0.8033414121551645,0.8025742887972849,0.8017531992978844,0.8008749959233625,0.7999365249049226,0.7989346676474798,0.797866390993888,0.7967288078936637,0.7955192499535355,0.794235353463178,0.792875160579843,0.7914372374008093,0.7899208106251536,0.788325924368381,0.7866536183936614,0.784906128493799,0.783087108910618,0.7812018754021737,0.779257665727829,0.7772639117593956,0.7752325139724527,0.7731781045614777,0.7711182797368974,0.7690737748959012,0.7670685485287339,0.7651297325333315,0.7632873992881707,0.7615740915043505,0.7600240628442592,0.758672190095713,0.7575525465766154,0.7566966756257278,0.7561316721118143,0.7558782588242013,0.7559491100745166,0.7563476938942838,0.7570678498753419,0.7580941928937057,0.7594032722155143,0.7609652794240025,0.7627460315198454,0.7647089650403908,0.7668169392924784,0.769033727962487,0.771325152385564,0.773659864087677,0.7760098170716044,0.7783504855173524,0.7806608855402156],[0.810407111757123,0.8100602421476428,0.8096800253313086,0.8092636606662457,0.8088082261652225,0.8083106947227636,0.8077679559908266,0.8071768449930243,0.8065341787408211,0.805836802309128,0.805081646041978,0.8042657957876215,0.8033865782987142,0.8024416641635073,0.8014291908356059,0.800347908467873,0.7991973512774376,0.797978036996286,0.7966916964850216,0.7953415346525907,0.7939325222238541,0.7924717153561194,0.7909685962785713,0.7894354225986724,0.7878875652261113,0.7863438045701572,0.7848265415010162,0.7833618637066084,0.781979390639651,0.7807118041174301,0.7795939627147654,0.7786615069250971,0.7779489049723542,0.7774869860095023,0.7773001698864931,0.7774038067561958,0.7778021951856969,0.778487815700825,0.7794420260512235,0.7806370319738738,0.7820386170969471,0.7836090405399705,0.7853096474308616,0.7871029473752136,0.7889540942852147,0.7908318127049667,0.7927088683379022,0.7945621938885183,0.7963727734198651,0.7981253712821715],[0.817103239212519,0.8171659809060793,0.8172169878463683,0.8172541416541543,0.8172751490360415,0.8172775415206959,0.8172586781358842,0.8172157517807996,0.817145800206292,0.8170457227058172,0.8169123038474987,0.8167422458481236,0.816532211507985,0.8162788799942945,0.8159790181800427,0.8156295707076155,0.8152277724345267,0.8147712873968337,0.8142583788315847,0.8136881150292437,0.8130606156760467,0.8123773426438163,0.8116414375197298,0.8108581050090815,0.8100350359541133,0.8091828551150471,0.8083155658342778,0.8074509448587932,0.80661081461032,0.8058210864104088,0.8051114278803245,0.8045143669319845,0.8040636200679653,0.8037914637177597,0.8037251360007583,0.8038826815283635,0.8042693296330526,0.8048759241850149,0.805680267932525,0.8066507414832255,0.8077506741049916,0.8089422328344157,0.8101892993571054,0.8114592984929113,0.8127241574040136,0.8139606264299203,0.8151501732466663,0.816278619371962,0.817335642996071,0.8183142330551172],[0.8240006087702131,0.8245002806159222,0.8250129027210394,0.8255373575891497,0.8260723310479419,0.8266162982677197,0.8271675100373944,0.8277239796115594,0.8282834705373314,0.828843485992554,0.8294012603256632,0.8299537536920071,0.8304976509438489,0.8310293662662375,0.8315450554750599,0.8320406384251651,0.8325118346334106,0.8329542160186649,0.8333632816034903,0.8337345600969973,0.8340637474361571,0.8343468874935706,0.8345806050522815,0.8347624004305323,0.8348910141918638,0.8349668672108941,0.8349925744712692,0.8349735181371734,0.8349184435973855,0.8348400074048654,0.8347551539138552,0.834685124218976,0.8346548062401268,0.8346910264629638,0.8348192939975577,0.8350585878951621,0.8354148406696847,0.8358771339764588,0.8364208177127979,0.8370143550067056,0.8376251895007905,0.8382234942789535,0.8387841433476004,0.8392874336995351,0.8397190163491629,0.8400693831980738,0.8403331499200134,0.8405082880691386,0.8405953953398483,0.8405970489230582],[0.8309280731325142,0.8318757661406322,0.832862675497442,0.8338888789898399,0.8349542609814453,0.8360584882144986,0.837200983641078,0.8383808981793457,0.8395970803043059,0.8408480434087491,0.84213193091456,0.8434464791858911,0.8447889784053702,0.8461562317382864,0.8475445133486673,0.8489495261730572,0.8503663608383212,0.8517894577739471,0.8532125754712724,0.854628769044465,0.8560303848166195,0.8574090786471282,0.8587558681615037,0.8600612318988307,0.8613152714667778,0.8625079556301546,0.8636294669143856,0.8646706700123469,0.8656237139172798,0.8664827610225255,0.8672447981524283,0.8679104146825072,0.868484316993933,0.8689751747569648,0.8693941677859941,0.8697513690009865,0.8700492936406644,0.870277796365847,0.8704185164328985,0.8704523388896299,0.8703638925053848,0.8701434184678652,0.8697869750604125,0.869295748169173,0.8686749926354621,0.8679329186833074,0.8670796862113317,0.8661265736446812,0.8650853331808909,0.8639677165126741],[0.8377010165014922,0.8390897216570392,0.8405437053169651,0.8420642591432365,0.8436524931585245,0.8453093037293891,0.8470353379168495,0.8488309537827237,0.850696176186406,0.8526306475478975,0.8546335729903675,0.8567036592122391,0.8588390463798047,0.8610372322850794,0.8632949879930969,0.8656082642281441,0.867972087849054,0.8703804479826933,0.8728261717828688,0.8753007904437359,0.8777943971365219,0.8802955001063478,0.882790876451882,0.8852654353415114,0.8877021038435345,0.8900817543890752,0.8923832002486171,0.8945832940686853,0.8966571735512208,0.8985787053475267,0.9003211778242743,0.901858274690688,0.9031653049267646,0.9042205433378813,0.9050063503816037,0.9055096451468879,0.9057217381088615,0.9056384686718082,0.905261361374663,0.9045988169810679,0.9036660863410014,0.9024840146183433,0.901077227161398,0.8994723301954335,0.8976964138600698,0.8957759399737341,0.8937359920541448,0.8915998239081441,0.8893886347478599,0.8871215052395248],[0.8441357961257306,0.8459404130457681,0.8478343441806376,0.8498199219425555,0.8518992960038422,0.8540743934078725,0.8563468737233424,0.8587180786439629,0.8611889753460984,0.8637600928110404,0.8664314501939345,0.8692024761753202,0.8720719180616581,0.8750377392069488,0.8780970031094153,0.8812457422996078,0.8844788098896776,0.8877897114182078,0.8911704144366925,0.8946111332023646,0.8981000859632833,0.901623222794895,0.9051639229988989,0.9087026630416285,0.9122166593794881,0.9156794959919345,0.9190607550034386,0.9223256818064571,0.9254349355584256,0.9283445046930298,0.9310059095880325,0.9333668777426146,0.9353727704817351,0.9369691688925293,0.938106141625995,0.9387445386477629,0.9388634074991353,0.938465075963926,0.937574148363217,0.9362313796077862,0.9344865608576304,0.9323928844781026,0.9300031502027686,0.9273674435349147,0.9245318586753193,0.9215379267443083,0.9184225008506475,0.9152179209009538,0.9119523349100072,0.9086500938242832],[0.8500643809760314,0.8522437011584526,0.8545327735361063,0.8569346363168473,0.859452112354398,0.8620877588571684,0.8648438107975375,0.8677221173151011,0.8707240703148358,0.8738505243518695,0.8771017067650767,0.8804771168676878,0.8839754128198077,0.8875942845898106,0.8913303111536917,0.8951787997791789,0.8991336048925361,0.903186923633979,0.9073290647861612,0.9115481873423618,0.9158300046335291,0.9201574497806179,0.9245102985014493,0.92886474635771,0.9331929400096317,0.9374624669828155,0.9416358174851773,0.9456698474898686,0.9495152984536435,0.9531164711786285,0.9564112168436573,0.9593315059146209,0.961804973415438,0.9637580183693056,0.9651212411636404,0.9658381924186275,0.9658783737886362,0.9652500566178355,0.963996144983835,0.9621795437903055,0.9598717676299189,0.9571455345446475,0.9540703297844713,0.9507100449512238,0.9471219818460604,0.9433566958143443,0.9394583133724286,0.935465084153201,0.9314100185851624,0.927321525613482],[0.8553469810426312,0.8578473485602848,0.8604732354480775,0.8632279597214771,0.8661145516301333,0.869135689446512,0.8722936274221905,0.8755901151402233,0.8790263074241179,0.8826026638902155,0.886318837150212,0.8901735485837119,0.8941644505072,0.8982879734658095,0.9025391572696476,0.9069114642903274,0.9113965734329632,0.9159841531170446,0.9206616115596391,0.9254138226976091,0.9302228262827542,0.9350675011570664,0.9399232116701565,0.9447614289825681,0.9495493321795091,0.9542493996355316,0.9588190104268107,0.9632100911420601,0.9673688687579399,0.9712358304119009,0.9747460525786221,0.9778301526968352,0.9804162407908773,0.9824334017704771,0.9838173783387045,0.9845190362032592,0.9845148706635349,0.98381442719005,0.9824576126084411,0.9805042966087261,0.9780238573887651,0.9750877636513128,0.9717650693180111,0.9681200269703294,0.9642110753169028,0.9600906395418245,0.9558053657775678,0.9513965550803369,0.9469006628889607,0.9423497941167703],[0.8598807970641205,0.8626408093918471,0.8655369993992545,0.8685725396728675,0.8717502087378328,0.8750723107333189,0.8785405857412765,0.8821561099967112,0.8859191851906061,0.8898292160737943,0.8938845755874691,0.8980824567913671,0.902418710944955,0.9068876712342497,0.9114819618467477,0.9161922924051124,0.9210072382117722,0.9259130073783323,0.9308931967785103,0.9359285399554569,0.9409966517453515,0.9460717765963076,0.9511245505563422,0.9561217909209058,0.9610263328753492,0.9657969395113047,0.9703883207724352,0.974751308679557,0.9788332511079278,0.9825787048968112,0.9859305312479038,0.988831520614119,0.9912266925715449,0.993066400167799,0.9943102407793912,0.9949313965600666,0.9949203416928198,0.9942863258781025,0.9930556481061042,0.9912674444475857,0.988968835389823,0.9862108744914726,0.9830457352151033,0.9795249420145572,0.9756983001228203,0.9716132489595132,0.9673144696037221,0.9628436529592429,0.9582393781541745,0.953537071965673],[0.8636038273921565,0.8665592580684028,0.8696566039575969,0.8728985526209049,0.8762872756429166,0.8798243332383375,0.8835105685277087,0.8873459908397203,0.8913296474587836,0.8954594833370959,0.8997321884434839,0.9041430326437728,0.9086856883213926,0.9133520413805102,0.9181319918640481,0.9230132462120008,0.9279811042411207,0.9330182453200251,0.9381045200361887,0.9432167560146802,0.9483285895811427,0.9534103388029034,0.9584289382225943,0.9633479614013036,0.9681277641692045,0.9727257889251558,0.9770970775846335,0.9811950460191831,0.9849725725205444,0.988383440612191,0.9913841419235041,0.9939359724940503,0.9960072287452311,0.9975751239662961,0.9986268538256213,0.9991592120886822,0.9991765829748152,0.9986880949161955,0.9977055095325729,0.9962429337632106,0.994317944455317,0.9919528495021085,0.9891751848710107,0.9860173067668507,0.982515368762118,0.978708039893048,0.9746352246714627,0.9703369305019165,0.9658523422198445,0.961219111926008],[0.8664937202751449,0.8695818800491877,0.8728134435521746,0.8761904126809928,0.8797141596747388,0.8833853214045222,0.8872036833866013,0.8911680531820927,0.8952761230067181,0.8995243215976411,0.9039076556892268,0.9084195418574069,0.9130516300308671,0.9177936206699375,0.9226330785217357,0.9275552470217873,0.932542868885009,0.9375760202775667,0.9426319682554013,0.9476850639635986,0.9527066874686827,0.9576652640631893,0.9625263763859546,0.967253001553505,0.9718059072731595,0.9761442447872463,0.9802263780297451,0.9840109851362668,0.9874584565688941,0.9905325877087305,0.9932025142755021,0.9954447545433729,0.9972450875325173,0.9985997921862766,0.9995154835782707,1.0000064575036574,1.0000885495347476,0.9997707394085233,0.9990507103653984,0.9979192718927747,0.9963686449006398,0.9943982000007817,0.9920165561036636,0.9892413108895419,0.9860976245417402,0.9826164051034798,0.9788324915582121,0.9747830226421602,0.9705060645543847,0.9660395098727573],[0.868562639374112,0.8717256224752139,0.8750301821362588,0.8784775828856587,0.8820683750890357,0.8858022861686841,0.8896781028157261,0.8936935443087347,0.89784512731153,0.9021280228599109,0.9065359066802,0.9110608045320434,0.9156929349580158,0.9204205526795433,0.925229796931462,0.9301045503052826,0.9350263152006761,0.9399741167852853,0.9449244434378516,0.9498512379740622,0.9547259554549498,0.9595177059045323,0.9641935025500965,0.9687186378069176,0.9730572094802962,0.9771728175492501,0.9810294460227273,0.9845925328620474,0.9878302115679206,0.9907146782613611,0.9932235957684614,0.9953413903088559,0.9970602278916066,0.99838037907399,0.9993095890372973,0.9998609149855044,1.000047995422605,0.9998754599499249,0.9993312964263898,0.9983975534973626,0.9970610496390798,0.9953170163240728,0.9931697535492692,0.9906320467843519,0.9877239949700465,0.9844715811584391,0.9809051897144592,0.9770581971854259,0.9729657099054496,0.9686634832105547],[0.8698497356068255,0.8730363338288787,0.8763603316854351,0.879822324741719,0.883422150652264,0.8871587848239069,0.8910302292659688,0.8950333952207258,0.8991639804926567,0.9034163427978461,0.9077833709479738,0.9122563562794004,0.916824867449318,0.9214766325582623,0.9261974335273117,0.9309710187574726,0.9357790413131367,0.940601031166485,0.9454144113501161,0.9501945690824497,0.9549149938847685,0.9595474951474197,0.9640625111651261,0.9684295198526276,0.9726175575209784,0.9765958454270423,0.9803345133486924,0.9838053941684972,0.9869828424555569,0.989844502801595,0.992371920539315,0.9945508503962797,0.996371082576478,0.9978255826896106,0.9989087668328548,0.9996139365538249,0.999930800881024,0.9998468928612104,0.9993553048201373,0.9984553901057921,0.9971497771674138,0.9954445855649927,0.9933502460119348,0.9908818929316987,0.9880592519428909,0.984906148554632,0.9814497842839689,0.9777199031081737,0.9737479398415184,0.9695662128209949]],[[0.1345851521283475,0.13397995776700128,0.13339061038909922,0.1328225911550461,0.13228149756300472,0.13177294130326805,0.13130243433789268,0.13087526608472483,0.1304963754965416,0.13017022264085434,0.12990066501380884,0.12969084417396357,0.1295430882838845,0.12945883575177458,0.12943858436209818,0.12948186910837653,0.1295872704728327,0.12975245325373527,0.12997423436319416,0.13024867645229515,0.13057120289946886,0.1309367287239777,0.13133980141977528,0.13177474556042723,0.13223580527532955,0.1327172792793078,0.13321364396825627,0.13371966108032415,0.13423046747541756,0.1347416456268623,0.13524927438582435,0.13574996042782578,0.1362408514954958,0.13671963310195992,0.1371845107563937,0.13763418002713362,0.13806778688350585,0.13848488077306878,0.1388853628149074,0.13926943134017358,0.13963752680527566,0.139990277856573,0.14032845005218236,0.1406528984591452,0.14096452505393434,0.1412642415709631,0.1415529381759265,0.14183145809560183,0.14210057811884752,0.1423609946991151],[0.13149639044373349,0.1307109138741015,0.12994292717327052,0.1291998163186508,0.12848921639774358,0.12781887104862294,0.12719647042455545,0.1266294714064219,0.12612490552298244,0.12568918171069546,0.12532789246543538,0.1250456329073855,0.12484584261135916,0.12473067960984119,0.12470093469773517,0.12475599210212983,0.1248938398827066,0.12511113034863958,0.12540328762607555,0.1257646566092169,0.12618868516263956,0.12666812981810283,0.12719527442653833,0.12776215127733392,0.12836075498106936,0.12898324076189774,0.12962210052358603,0.13027031194064193,0.13092145770910515,0.13156981383559088,0.13221040735735243,0.1328390451216368,0.13345231619539571,0.1340475711379805,0.13462288177756618,0.1351769853228117,0.13570921665305682,0.13621943249992366,0.13670793099344228,0.1371753697250889,0.13762268510230607,0.13805101535427597,0.13846162911409238,0.13885586106295705,0.13923505569087619,0.1396005198174157,0.13995348413589245,0.14029507370389327,0.14062628700940866,0.14094798300022793],[0.1278909225882057,0.12687884159143883,0.1258846501051024,0.12491819808953236,0.1239898205428932,0.12311015013918226,0.12228989125822937,0.12153955942463085,0.12086919343307853,0.1202880508529073,0.11980430080053475,0.11942473038976913,0.1191544826445844,0.11899684348657608,0.11895309345912053,0.11902243614115071,0.11920201003987833,0.11948698469638805,0.11987073552066081,0.12034508625550142,0.12090060360336136,0.12152692586302395,0.12221310656066042,0.12294795489644669,0.12372035702992899,0.12451956534477937,0.12533544639511116,0.12615868182372683,0.12698091983982293,0.12779487764748068,0.12859439743189685,0.12937446012829334,0.13013116226742957,0.13086166179233927,0.13156409896525592,0.13223749842042784,0.13288165814492853,0.13349703074805355,0.13408460185822582,0.13464576989966015,0.13518223087512096,0.13569587113541404,0.13618867046667635,0.13666261718741016,0.137119636332387,0.13756153142377328,0.13798993980436736,0.13840630104585205,0.1388118375564809,0.13920754620478676],[0.12376126963686296,0.12246792303852658,0.12119043239043754,0.11994174324528722,0.11873569185040361,0.11758676936788474,0.1165098181131391,0.11551966182694837,0.11463067788924726,0.11385632624782555,0.11320865698570576,0.11269782488185547,0.11233164382421691,0.1121152153302825,0.11205066286461399,0.11213699688343191,0.11237012515478798,0.1127430102464844,0.11324596301012549,0.11386704938256431,0.11459257948235797,0.1154076437112517,0.11629666047507914,0.11724390359631687,0.11823398342731249,0.11925226286667441,0.12028519682434685,0.1213205903445246,0.12234777608389266,0.1233577159641289,0.12434303460947085,0.125297993820367,0.1262184180632817,0.12710158102029886,0.1279460628563416,0.12875158719706067,0.12951884598904775,0.13024931951569976,0.13094509791332462,0.1316087095967435,0.13224296107237385,0.13285079169489278,0.13343514601659537,0.13399886549545462,0.13454460048224767,0.1350747426166225,0.13559137704660923,0.13609625326567815,0.13659077285311394,0.1370759920193484],[0.11913808933025175,0.11750120734954193,0.11587388264004585,0.11427276645688406,0.11271607294171725,0.11122331493941623,0.10981492445261345,0.10851175093969129,0.10733444032564696,0.10630271072685538,0.1054345565727382,0.10474542904141612,0.10424745449667978,0.1039487603775904,0.1038529766062218,0.10395896843237816,0.10426083454637389,0.10474817569850126,0.10540660925908561,0.10621847978566719,0.10716369909695848,0.1082206435453823,0.10936704048137548,0.11058078770118118,0.11184066547948351,0.11312691729585267,0.11442169011081538,0.11570933666192766,0.11697659033294065,0.1182126279801708,0.11940903832028812,0.12055971383759682,0.12166068334063097,0.1227099008308356,0.12370700462267757,0.12465305891123041,0.12555028834137566,0.12640181463242756,0.1272114029434128,0.12798322439305404,0.1287216399348803,0.12943100959959264,0.1301155299368872,0.1307791013186166,0.13142522562294376,0.13205693373677094,0.13267674133035198,0.13328663051346604,0.13388805431105444,0.1344819604213655],[0.11410749229660992,0.1120600101408599,0.11000889644335617,0.10797486996405023,0.1059812691555534,0.10405383247082878,0.10222029674297357,0.10050978135966962,0.09895193788271932,0.09757586653961821,0.09640883312536011,0.09547485974050314,0.09479330380935479,0.09437757153627571,0.09423412259557072,0.0943619037208547,0.09475229905467099,0.09538961377813455,0.09625203167624923,0.09731292564473785,0.09854236611627744,0.09990866978180711,0.10137985431328371,0.10292490315049588,0.1045147863051625,0.10612321996174955,0.10772717496873072,0.10930716130152605,0.11084732372189138,0.1123353855981437,0.11376247564159113,0.1151228681437865,0.11641366254523011,0.11763442365263196,0.11878679994766807,0.11987413430663045,0.1209010790157092,0.12187322507060148,0.12279675421115506,0.12367812078922173,0.12452376926021742,0.125339891731142,0.12613222854619005,0.12690591335126933,0.12766536249816668,0.12841420710441792,0.12915526466658753,0.12989054592096222,0.13062129172868162,0.1313480341778824],[0.10883071482807798,0.10630727941807629,0.10375679184970935,0.10120370332371616,0.098676605300499,0.09620823117754604,0.0938352134199933,0.09159750692651289,0.08953738945037651,0.0876979710035159,0.08612119637042297,0.08484541328183133,0.08390269605889505,0.08331623435009801,0.08309817540140661,0.08324830059734241,0.08375380095557863,0.08459021428529526,0.08572336254865882,0.08711195668750929,0.08871046641550054,0.0904718866808735,0.09235013554695694,0.0943019425703448,0.09628819495719797,0.09827478283171956,0.10023302365760853,0.10213975725272963,0.10397719734686212,0.105732612108133,0.1073978904966714,0.10896903702886822,0.11044562598238904,0.11183023751976066,0.11312789234293114,0.11434549775347634,0.11549131576948257,0.11657446266629548,0.11760444847222372,0.11859076417173606,0.11954252336970377,0.12046816379000366,0.12137521217515478,0.12227011398072879,0.12315812686334571,0.1240432745420769,0.12492835538524297,0.12581499823421136,0.1267037566702687,0.12759423223967667],[0.10356242717468817,0.1005117663107849,0.09739710455869918,0.09424489500408187,0.0910875764230101,0.08796411230821162,0.0849203175763427,0.08200880044866528,0.07928828816295856,0.07682206373789661,0.07467525657208905,0.07291085654690928,0.07158460386557029,0.07073932828838272,0.07039974069831324,0.07056888222816605,0.07122720169296243,0.07233456468548162,0.07383468068010712,0.07566085788665451,0.07774188217310245,0.08000710348974799,0.08239026579183091,0.08483201594785349,0.08728127219086157,0.0896957272674218,0.09204175701672637,0.09429395461019645,0.09643444971278144,0.09845211814264257,0.10034174705160136,0.10210319301848103,0.10374055327172943,0.10526136071256226,0.10667580905454051,0.10799601332829095,0.10923531178885575,0.11040761682812839,0.11152682401662711,0.11260628927098962,0.11365838396259649,0.11469413635782566,0.11572296514104015,0.11675250715470353,0.1177885372994234,0.11883497426674215,0.1198939619319702,0.12096601323679855,0.12205020152115931,0.12314438362464206],[0.0986590958074995,0.09506406891233943,0.09135351396840034,0.08755213719827534,0.08369212798054665,0.07981455109071345,0.07597082523418465,0.07222412136321212,0.06865034496063252,0.06533811153164551,0.062386815103639734,0.059901673208992354,0.05798483999935243,0.05672274614680325,0.056171848770814964,0.056347057600017625,0.05721741589081842,0.05871105456757662,0.06072739692500558,0.06315198738467805,0.06586960727343852,0.06877345314511145,0.07177022779153082,0.07478209231227094,0.07774663932728308,0.08061581875237331,0.08335442272886406,0.08593846930710848,0.08835364776039983,0.09059388608945061,0.09266004846813349,0.09455874699368164,0.0963012450203066,0.09790243087295435,0.09937984657369422,0.10075276397545102,0.10204130892179945,0.10326564166673428,0.10444520788508493,0.1055980783996207,0.10674039667329913,0.10788595093407016,0.10904588272987695,0.11022853643339221,0.11143944578358553,0.11268144519939721,0.11395488650224898,0.11525793672481767,0.11658693031912645,0.11793674930175357],[0.09456215185207488,0.09046598973865494,0.08619339709183856,0.08176218342724115,0.07719753078480118,0.07253401676093636,0.06781826081309089,0.0631123540450676,0.0584981612541852,0.054082292690917154,0.050000751272796976,0.04642056321217863,0.04353300972217592,0.041531121453887036,0.04056819849397587,0.04070923472091825,0.041903465882703377,0.04399898175985094,0.046788861714955866,0.050059095632731844,0.053618857078490074,0.05731211264584607,0.06101784163899743,0.06464555257074694,0.06812982891863481,0.07142541996266433,0.07450326636931581,0.07734740367679316,0.07995255835128123,0.08232224537644074,0.08446720793133065,0.08640407671131918,0.08815415942584989,0.08974229880004768,0.09119576123444441,0.09254313946732724,0.09381327175167152,0.09503419689107699,0.09623217785594207,0.09743083506162332,0.09865043228984628,0.09990735295937213,0.10121379249485735,0.10257767574079443,0.10400278959965367,0.1054891035943475,0.10703323769350899,0.1086290292499623,0.11026814969033452,0.11194072583424057],[0.09173757306029799,0.08726636272600027,0.08256340790463847,0.0776364560344728,0.07249835020381662,0.06716855924974587,0.06167538848309113,0.05605932121162621,0.05037829713564648,0.04471637266012477,0.03919824931002071,0.03401327597634814,0.029450801317157736,0.025931827382274654,0.023966314953978714,0.02392467539863741,0.025741458042729096,0.028951441417015313,0.03300861089172481,0.037487268317348534,0.042102906581057156,0.046673337055403635,0.051082151998224634,0.055254994219990174,0.059145475752410075,0.06272689091643024,0.06598721650836267,0.06892596251888616,0.07155206742019142,0.0738823765465282,0.07594042801374458,0.07775537300832727,0.07936091708875463,0.0807942087017308,0.08209463275884764,0.08330249738167801,0.08445763328972987,0.08559795686382458,0.0867580758687681,0.08796803551641713,0.08925230633996127,0.09062910091097942,0.09211007472748899,0.09370042341481262,0.09539934289009783,0.09720078102306536,0.09909438567814612,0.10106654748374234,0.10310144438671953,0.10518201415173059],[0.09056695112465815,0.08592854240881126,0.08102972296270664,0.0758714799194521,0.07045762009890877,0.06479527333248884,0.05889549646594292,0.05277404013977669,0.0464524135316571,0.03995956745370546,0.033335038393043914,0.02663608929229289,0.01995800683678242,0.013510233332046864,0.008020973153915178,0.006552024049538051,0.010676252503246919,0.016422021100298983,0.02234702590872058,0.02811584090655121,0.033604767367268716,0.03875069003579882,0.043516471606170094,0.04788025113101487,0.051831335954203625,0.05536834431165892,0.058498243424705575,0.061235778352107514,0.06360306638724428,0.06562923097471693,0.06734998371101106,0.06880707318535025,0.0700475224546028,0.07112258300603627,0.07208635017207396,0.07299401959540083,0.07389981954395206,0.07485472602203228,0.07590414370856197,0.07708579397873748,0.07842806725006879,0.07994905468406273,0.08165637682228694,0.08354779844607488,0.08561249672918313,0.08783276691507098,0.09018592247697575,0.09264617055552733,0.09518629985606358,0.09777908508372037],[0.09122396696494908,0.0866680106487009,0.08186260273886789,0.07681055809997181,0.0715179871108215,0.06599499817412488,0.06025661889682037,0.05432408858795688,0.04822683413903717,0.04200581119080171,0.03571981925983298,0.029458933939703818,0.023376772938219176,0.01777697026127422,0.013345483727259282,0.011458948179393724,0.013070283296184917,0.016986547255007273,0.021761830318735773,0.026705418581615632,0.03152032032461648,0.03606267970394488,0.040254320599052894,0.04405060526692676,0.04742738902624426,0.050375206254155376,0.05289650407107187,0.0550042898068615,0.0567214785744232,0.05808058011260264,0.0591234974368331,0.0599012486737506,0.060473419205580047,0.06090713301071102,0.061275326759651375,0.061654149701113034,0.062119429640202645,0.062742357071952,0.06358481867594341,0.06469506810362993,0.06610452443588016,0.06782633617803983,0.06985595698160206,0.07217349880061415,0.07474725906018033,0.0775376867938092,0.08050115130111332,0.08359310356157411,0.08677046022827292,0.08999322056779308],[0.09360685061912907,0.08935978793089845,0.0849071233723909,0.08025954030169158,0.07543300735638507,0.07045015367728101,0.065342120860957,0.06015112106241068,0.05493404398685194,0.04976758901054139,0.04475545667703492,0.04003775598437139,0.03580092283861702,0.03228092170114151,0.02974198658980537,0.028408172350131947,0.028358333072878255,0.029464309801184006,0.03144165543703379,0.033962952971593505,0.03674043821199432,0.03955301098004115,0.04224157316460636,0.0446956202187892,0.046840946651071094,0.04863073698756324,0.05003972865554226,0.051060649361770884,0.051702245972932534,0.05198841472500006,0.051958075532969036,0.05166547923408466,0.05118059070785837,0.05058905220906614,0.04999101993599796,0.049497966424288956,0.04922655067203346,0.04928918025877109,0.04978212988478095,0.050773730361128776,0.05229616026460316,0.05434362972545054,0.05687730285224301,0.059834729165561304,0.06314048342483661,0.06671537782838977,0.07048303695318142,0.07437381944429261,0.07832666572729648,0.08228956654359497],[0.0973755722656147,0.0935894913903811,0.0896544894733953,0.08558836485251563,0.08141488929958626,0.07716497196853038,0.07287799174192255,0.06860325715477884,0.06440146614968734,0.06034587083587402,0.05652256575945393,0.05302890192219014,0.04996859771064843,0.04744206989958832,0.045531577834193294,0.0442835193541202,0.04369369740467163,0.04370250233900457,0.04420314996059717,0.04505948228247509,0.04612589457299765,0.04726322317137192,0.0483483503405909,0.04927837524038996,0.04997132327098004,0.05036518304473118,0.05041647131761655,0.05009901062890303,0.04940328542817715,0.04833659189251181,0.046924153921679264,0.04521138401392897,0.04326745091007343,0.041190142030358895,0.03911139963336396,0.03720138518829431,0.035666083729443646,0.03473036267502692,0.034600093138545264,0.03541056372206102,0.037188258127010536,0.039852559310226146,0.04325375597417531,0.04721914613445385,0.05158515915726356,0.0562118186374727,0.0609855553801484,0.0658167204929664,0.07063556020943328,0.0753882955873398],[0.10206690016793019,0.0988069868294033,0.0954498244824119,0.0920159047673519,0.08853067824243739,0.08502502486501534,0.08153558706639336,0.07810484332993904,0.07478074822920633,0.07161571186252212,0.06866466001777465,0.06598194737626303,0.0636170450521124,0.06160923331411298,0.059981974226602675,0.0587380655968252,0.0578568276965388,0.05729423374826436,0.056986108175131986,0.05685363745037798,0.05680990283980627,0.056766152339175785,0.05663694733510539,0.05634385353175776,0.05581776351531218,0.05500016096011202,0.053843698602018084,0.05231243739667497,0.05038204816763594,0.048040255353799334,0.04528784181666345,0.04214068345718122,0.038633640888072425,0.034827916072952755,0.030825123129687777,0.026794485433592755,0.023023550026724175,0.0199942736962945,0.018404201507241574,0.018877840359133435,0.021431110733079812,0.02551061779840091,0.03051322332159478,0.03602097789322708,0.041776625588632654,0.047620589129344804,0.053449331540634346,0.05919253728836546,0.06480081974917072,0.07023885666525166],[0.10721519943047123,0.10447760114625344,0.10168123976556055,0.09884533622667105,0.0959924284949409,0.09314831328434982,0.09034177644906902,0.0876040389813227,0.0849678436743479,0.08246612061659939,0.08013020613464414,0.0779876559366914,0.07605978784577004,0.07435919767157098,0.07288758199119551,0.07163423266100623,0.07057550704479706,0.06967542347856862,0.06888732327082724,0.06815634628257103,0.06742234940286994,0.0666228831129099,0.06569591490662192,0.064582107186708,0.06322657732790997,0.061580160251543045,0.059600249542688256,0.057251315999428246,0.05450520263505648,0.051341282940098536,0.04774655270136142,0.043715710375450384,0.03925127127250831,0.034363763282591796,0.029072086145303374,0.023404260015659477,0.017399439455986092,0.011116207455481978,0.004708851935980792,0.0028445924564589253,0.009360489873444705,0.01622997128114702,0.023126020384120698,0.029972582605378197,0.03671918522771375,0.04332603609713551,0.0497608220468053,0.05599742594951634,0.06201513308602183,0.06779800616332168],[0.11242982330912411,0.11016885083554677,0.10787394040726293,0.105560975336303,0.10324770126995277,0.10095343358238876,0.09869859676181057,0.09650407145034322,0.09439033629936297,0.09237641136745868,0.09047863765857345,0.08870936145914625,0.08707562709492779,0.08557800925429432,0.08420972643989702,0.08295616270606962,0.08179488371354941,0.08069617157186099,0.07962403451451959,0.07853758860842967,0.07739267277780743,0.07614355115190914,0.0747445753207053,0.07315171476992284,0.07132390614903593,0.0692242127190423,0.06682081999195322,0.06408792233563622,0.06100658256051917,0.05756568137665381,0.05376313298866883,0.04960766028875094,0.04512167026683458,0.040346315773593,0.035351086716756484,0.030253265568975566,0.02525956459761184,0.02075483076218926,0.017450539606249427,0.016372099051513576,0.018083602320739724,0.02199494360221516,0.027156745443417275,0.03293252614251703,0.03897582941876693,0.04509541720552513,0.05117778833213575,0.05715063015440801,0.06296543893849037,0.06858873449537763],[0.1174237440809059,0.11557472979109354,0.11370585874270188,0.11182916668006236,0.10995753775614323,0.1081043683219576,0.10628312428366118,0.10450679115574206,0.1027872258339256,0.10113443168439,0.09955579273636647,0.09805531664191484,0.09663294696078872,0.09528401030543056,0.09399886052675537,0.09276276943953486,0.09155609266294693,0.09035471322774848,0.0891307393942439,0.08785341158010261,0.08649016023643695,0.0850077537172402,0.08337348224822311,0.08155633898449077,0.07952817920357394,0.07726486168569711,0.07474740129995742,0.07196318952786313,0.06890737302991853,0.06558452476892249,0.0620108056825193,0.058216907310459094,0.05425219335755099,0.05019060207665065,0.04613891845396161,0.04224757795781821,0.038722143412203126,0.03582796480066386,0.03387053630353306,0.03313013513512128,0.03375976729991973,0.03571635749635242,0.03879109349334996,0.042706182281132384,0.04719705170800906,0.05204793416573981,0.05709516477720215,0.06221823703832858,0.06732924310887084,0.07236416993424132],[0.12201020981136482,0.12050430195568716,0.11898533436777047,0.11746183264653424,0.11594256016471846,0.1144362227688147,0.11295111398067263,0.11149470747468757,0.11007320973836603,0.10869109247297144,0.10735063069318826,0.1060514776559511,0.10479031062759263,0.10356058117266416,0.10235239961304467,0.10115257568407479,0.09994482704283164,0.09871015562009264,0.09742738065397831,0.09607380836285109,0.09462601296183755,0.09306070280514596,0.09135564885147378,0.08949065984857776,0.08744859875206629,0.08521644701927751,0.08278643675448157,0.08015728452051073,0.07733557402284869,0.07433734575754837,0.07118995513285334,0.06793424521366477,0.06462702242660762,0.06134367864854949,0.058180499035577385,0.0552556484159418,0.05270703664619662,0.05068454139494632,0.04933437712625864,0.048776166517249565,0.04907864412567228,0.050244286228276355,0.05221084214287913,0.054868620163031775,0.05808438436550619,0.061722303723396967,0.0656574169101773,0.06978188712550942,0.07400637365283724,0.07825882187783305],[0.12608495812541587,0.1248570740435288,0.12361847344477758,0.12237483206654494,0.12113174133242964,0.11989447843005721,0.11866774650372888,0.11745539270606901,0.11626011525914867,0.11508317396311163,0.11392412135541195,0.11278057353159927,0.11164804009707305,0.11051983156559415,0.10938705970068963,0.10823874201408652,0.10706201635021148,0.10584246585200593,0.10456454936096962,0.10321212814614168,0.10176907730385226,0.10021996948631748,0.09855081977535121,0.09674988321291468,0.09480850018704154,0.09272198878601774,0.090490586361995,0.08812044349581871,0.08562467029723585,0.08302442443287379,0.08035000783372409,0.07764189821807942,0.07495157459883828,0.07234189675777938,0.069886670999063,0.0676689076984478,0.06577722650112726,0.06430002450530033,0.0633175335675311,0.06289276633978026,0.06306328425393022,0.06383610108774986,0.06518734949067796,0.06706674919318148,0.0694053143953923,0.07212402084574258,0.0751415001621611,0.07837973964273538,0.08176763100698607,0.08524272521473582],[0.1296050511326906,0.12859730446005954,0.1275786856251964,0.126552716281343,0.12552269450780712,0.12449152853016607,0.12346155762831593,0.12243436679825927,0.1214106035469292,0.12038980678688024,0.11937025896422826,0.11834887311439089,0.11732112635397143,0.11628105031516614,0.11522128724003282,0.1141332180100943,0.1130071655208545,0.11183267381328263,0.11059886055484812,0.10929483809502942,0.10791019659195462,0.1064355416802404,0.10486307873798192,0.10318723576564473,0.10140531679954543,0.09951817706633909,0.09753090897878462,0.09545352361306914,0.09330160432729445,0.09109689637491869,0.08886777753087058,0.08664952935542544,0.08448429806920303,0.0824206030939423,0.08051223119010464,0.07881636360563062,0.0773908474846872,0.07629066230836698,0.07556384636418222,0.0752473918387657,0.0753637948670726,0.07591894739143208,0.07690182430544334,0.07828601016241343,0.08003268461621242,0.08209441396833991,0.08441905623497438,0.08695323902160207,0.08964510628159736,0.0924462509888564],[0.1325696425352177,0.13173217166802914,0.13088236759975494,0.13002220094584946,0.12915338566149295,0.12827726586050492,0.12739469908734385,0.12650594103980112,0.1256105376852675,0.12470723146630065,0.12379388875927175,0.12286745585423674,0.12192395041224349,0.12095849461261984,0.11996539505547549,0.118938273005027,0.11787024685391785,0.11675416688369203,0.11558290061713525,0.11434966540512129,0.11304840341822064,0.11167419291141775,0.11022368841204067,0.10869558117801434,0.10709106963798865,0.10541432724035067,0.1036729518427953,0.10187837610552578,0.10004621202844914,0.09819649474004423,0.09635378130230367,0.09454705082684185,0.09280934496661428,0.09117708672268952,0.0896890258021719,0.0883847863436012,0.08730304186616213,0.08647941170928876,0.08594425285071317,0.08572059019228874,0.08582246025140187,0.0862539152070705,0.08700884168198258,0.08807161183471542,0.08941844300660257,0.09101923803743696,0.0928396365385002,0.09484302793131144,0.09699234004336872,0.09925149553434083],[0.13500456844296704,0.13429505509927198,0.13357107562342374,0.13283351797531642,0.13208303635958565,0.13131997933397896,0.13054431910522513,0.12975558561456085,0.12895280949284035,0.12813447830332647,0.12729851064436104,0.1264422526187839,0.12556250087099355,0.12465555584244904,0.12371730811786075,0.12274335976051709,0.12172918141223228,0.12067030471273092,0.1195625483223467,0.11840227454408668,0.11718667224662617,0.11591406046898908,0.11458420568814515,0.11319864416971791,0.11176099899532498,0.11027727916014357,0.10875614547938545,0.10720912492113262,0.10565075151722199,0.10409860852987174,0.10257324371257183,0.1010979283289351,0.09969823251814033,0.09840139634460625,0.09723548911076582,0.096228370220505,0.09540649245830529,0.0947936199524391,0.09440956246883611,0.09426904711112086,0.09438085012474037,0.09474729064238017,0.09536414613508049,0.09622099403061321,0.09730192797690292,0.09858655333749823,0.10005114325436894,0.10166983591569816,0.10341577131889124,0.10526209414656659],[0.13695097772598358,0.13633363380190375,0.1356992804690558,0.1350480559260544,0.13437991250628992,0.13369457580056338,0.13299150721354897,0.1322698724591565,0.1315285187216626,0.1307659633340047,0.12998039682962262,0.12916970309267603,0.12833149905349653,0.12746319595014888,0.12656208360970592,0.125625438508174,0.12465065556457906,0.12363540273254968,0.12257779648927518,0.12147659529811568,0.12033140703931287,0.1191429052547952,0.1179130478207769,0.11664529032482296,0.11534478496726816,0.11401855423600335,0.11267562696560973,0.11132712280062443,0.1099862697483007,0.10866833876070965,0.10739047959700405,0.10617144417087364,0.1050311878245727,0.10399034604214824,0.10306959427046108,0.1022889114328553,0.10166678224595482,0.1012193874992104,0.10095984218909376,0.10089754577935459,0.10103770453296969,0.10138107209937217,0.10192393282851621,0.10265832622176985,0.10357248534734169,0.10465144162661097,0.10587773635708504,0.10723217669895857,0.10869457949671446,0.11024445767505857],[0.13845751330210168,0.13790197464228005,0.13732651055860326,0.13673072302811928,0.13611408263711924,0.1354759107133089,0.13481536588486595,0.13413143676281863,0.13342294252057021,0.13268854315298187,0.13192676112547252,0.13113601596223584,0.13031467306664102,0.12946110771479788,0.1285737847175299,0.12765135371214334,0.12669275943102476,0.1256973656076455,0.12466509042987765,0.12359655064205909,0.12249321053580159,0.12135753115941944,0.12019311412362098,0.11900483340043873,0.1177989475312233,0.11658318372945915,0.1153667845711597,0.1141605074406759,0.112976566826328,0.11182851017354047,0.11073101957511024,0.10969963438121302,0.10875039405534058,0.10789940634413263,0.10716235287091326,0.10655395205979837,0.10608740692112213,0.10577387143154993,0.1056219726508368,0.10563742514901364,0.1058227691440349,0.1061772541875251,0.10669687743815588,0.10737457143172423,0.10820052301683519,0.10916259477687751,0.11024681411973847,0.11143789368248658,0.11271974928612533,0.11407598728589965],[0.13957532540847659,0.1390556810203373,0.138512744673607,0.1379456975962953,0.13735364004338763,0.13673559059122953,0.1360904903401269,0.1354172131625576,0.13471458312809603,0.13398140017815072,0.13321647500708597,0.13241867392604192,0.13158697423846322,0.1307205303407211,0.1298187503779494,0.1288813828367847,0.12790861194706074,0.12690116019883957,0.12586039566582724,0.12478844116905612,0.1236882816259876,0.1225638652243427,0.1214201933583712,0.12026339359998543,0.1191007693955526,0.11794081974869948,0.11679322196197765,0.11566877068319134,0.1145792671752134,0.11353735405125148,0.11255629282838757,0.11164968464054482,0.11083113831317519,0.11011389458614619,0.10951042024221405,0.10903199072015035,0.10868828376397945,0.10848700901563009,0.10843359851665864,0.10853098043143265,0.10877945294781304,0.10917666775563899,0.10971772369496052,0.11039536231689202,0.11120024942933394,0.1121213211740823,0.11314617033144132,0.11426144840876784,0.11545326124717131,0.11670753970613716],[0.14035518022215257,0.1398492390310762,0.13931607288420952,0.13875448099220514,0.13816322176524573,0.13754102512871497,0.1368866101530845,0.13619870879086413,0.13547609645964764,0.13471763011339208,0.13392229429906016,0.13308925549847703,0.13221792480260586,0.13130802865553537,0.13035968703772668,0.12937349803339354,0.12835062724786878,0.12729290001213336,0.1262028937407795,0.12508402720781228,0.12394064288852592,0.1227780779094115,0.12160271858607323,0.12042203305905409,0.11924457622295886,0.11807996106681455,0.11693879080203756,0.11583254686004067,0.11477342910739541,0.11377414654812067,0.1128476594105902,0.11200687682159305,0.1112643181077051,0.11063174984734338,0.1101198146915264,0.10973767112733182,0.10949266518430406,0.10939005506294489,0.10943280748359861,0.10962148021998722,0.10995419917352826,0.11042673117956832,0.111032646444259,0.11176355804614764,0.11260942108612639,0.11355887130541167,0.11459958241230885,0.1157186227226711,0.11690279454575288,0.11813894344930706],[0.14084599624446895,0.14033481714145282,0.13979181400799706,0.1392153858341646,0.13860391690048363,0.13795579910549602,0.13726946016952396,0.13654339835224064,0.13577622424681562,0.13496671009848202,0.13411384693492395,0.13321690958469876,0.13227552939315426,0.13128977411871712,0.13026023410262627,0.12918811335007918,0.1280753236402848,0.12692457920000919,0.12573948883727307,0.12452464175285477,0.12328568255021387,0.12202937028486478,0.12076361578359288,0.11949749099337306,0.11824120388277255,0.11700603253066473,0.11580421263182902,0.11464877386643238,0.11355332254591267,0.11253177074059705,0.11159801570629338,0.11076557771798783,0.1100472090799714,0.10945449162385,0.10899744378910861,0.10868416069931608,0.1085205108644586,0.10850991085243591,0.10865319445383069,0.10894858593869103,0.10939177881330049,0.10997611313448184,0.11069283706889119,0.11153143292789772,0.11247998491117751,0.1135255653437869,0.11465461797255903,0.1158533203011131,0.11710791127942127,0.11840497525129177],[0.14109423987149033,0.14056190255230427,0.13999243100571265,0.13938376741701056,0.1387338486512226,0.13804063612272907,0.1373021523317605,0.13651652471934125,0.13568203742225896,0.13479719140022026,0.1338607732511928,0.13287193281996154,0.13183026943043155,0.13073592622491334,0.12958969166405943,0.12839310672019236,0.1271485756767832,0.1258594777231939,0.12453027570737524,0.12316661748999883,0.12177542435536157,0.12036495992131861,0.11894487202383884,0.1175261992381246,0.11612133318581765,0.1147439277590919,0.11340874709825943,0.11213144583971495,0.11092827803562666,0.10981573538472453,0.10881012099150433,0.10792707152545515,0.10718104779954536,0.10658482051364686,0.10614898305018762,0.10588152555043391,0.10578750306473034,0.10586882493886947,0.10612418313727583,0.10654912509958378,0.10713626378198646,0.1078756057544415,0.10875496933979158,0.10976045985751087,0.11087696830137447,0.11208866269723507,0.11337944690040842,0.11473336845785062,0.11613496423072427,0.11756953887994676],[0.14114371870482645,0.14057727928513308,0.13996771932163105,0.13931244752558652,0.13860885824887417,0.13785436644396146,0.13704645024336576,0.13618270196764037,0.13526088833494002,0.1342790205726017,0.13323543501222523,0.13212888457266478,0.13095864128607276,0.1297246096839595,0.12842745041383838,0.12706871288061505,0.12565097497704106,0.12417798706088322,0.12265481623261597,0.12108798565423814,0.11948560213098927,0.11785746348440815,0.11621513545131203,0.1145719860851395,0.11294316413389452,0.11134550694596253,0.10979736354591299,0.10831832015621895,0.1069288191820775,0.10564966900586338,0.10450145106653037,0.10350384233682393,0.10267488444577515,0.10203024349214142,0.10158251454352449,0.10134062919273444,0.10130942117085626,0.10148939309882204,0.10187670814745158,0.10246340674801953,0.10323782483979903,0.10418517076358057,0.10528820593117123,0.10652797101377127,0.10788450381910687,0.1093375050780622,0.11086692127540247,0.11245342687900811,0.1140787999808301,0.11572619443545057],[0.14103542264056937,0.14042497268314202,0.13976486784102868,0.13905190546506882,0.1382828405923097,0.13745442321623252,0.13656344410281115,0.13560679021748476,0.13458151085671025,0.13348489557939913,0.13231456499738856,0.13106857539590955,0.12974553799625946,0.12834475341965762,0.12686636153314848,0.12531150631735608,0.12368251464529363,0.12198308684600123,0.1202184955837512,0.11839578784653546,0.11652398264486184,0.11461425433184931,0.11268008827232945,0.11073739200148704,0.10880454125325133,0.10690233674786621,0.10505384513611694,0.10328409707222605,0.10161961841365007,0.10008777856214147,0.0987159542733779,0.09753052831283661,0.09655576890336412,0.0958126644481605,0.09531781258557495,0.0950824759320454,0.09511191242844122,0.09540506318679966,0.09595463800996037,0.09674758690096767,0.0977658966394011,0.09898761573154871,0.10038799506437987,0.10194063568828372,0.10361855455479593,0.1053951065111952,0.10724472940453725,0.1091435037600035,0.11106953666761969,0.11300319085069248],[0.1408071830482188,0.14014591278260974,0.1394281248569755,0.13864994545908346,0.13780741312767672,0.1368965151714177,0.13591323326672364,0.1348535995814314,0.13371376488751074,0.132490080234744,0.13117919384980767,0.12977816498901623,0.12828459649012483,0.12669678771361606,0.1250139094012759,0.12323620166056722,0.12136519574065423,0.1194039594105537,0.11735736446460643,0.11523237301555872,0.11303833660735152,0.11078729857629324,0.10849428529131902,0.10617756573277033,0.1038588512794282,0.1015633988124652,0.09931997109247725,0.09716060044759918,0.09512009791195693,0.09323525414595497,0.09154369571831249,0.09008239515523447,0.08888588710270848,0.08798431123331941,0.08740147155854724,0.08715315004752824,0.08724591685901836,0.0876766264565305,0.08843268420564501,0.08949303858209265,0.09082973767072258,0.09240981727744718,0.09419727480596916,0.09615491992612303,0.09824595858735528,0.10043523794570491,0.10269013963763486,0.10498115003649734,0.1072821585563469,0.10957054268020375],[0.14049305402342224,0.13977721448553188,0.13899795778284038,0.1381507152415363,0.13723077218927301,0.13623330030438438,0.13515339922318167,0.1339861489661624,0.13272667495047177,0.1313702275818093,0.12991227866216826,0.12834863710562486,0.12667558671389528,0.12489004901112526,0.12298977434797242,0.12097356461825823,0.11884153092487822,0.11659538929011909,0.11423879688638003,0.11177773005574586,0.10922090328543184,0.1065802248786105,0.10387127971614522,0.10111382148003319,0.09833224510044285,0.09555599410408608,0.09281983648456828,0.09016391734657088,0.08763347000728955,0.08527804679631479,0.08315012962588712,0.08130301723543844,0.07978798022666934,0.07865083448027835,0.07792828714998974,0.07764459512066517,0.0778091526670307,0.07841551871167743,0.07944210469128433,0.08085436809845456,0.08260804123510761,0.08465278126779956,0.08693567496783856,0.0894042050462334,0.09200849226372304,0.09470279879553506,0.0974463851469626,0.10020385910632784,0.10294515930559807,0.10564529750589835],[0.14012246373558113,0.13935113551338985,0.1385097791114681,0.13759315677153716,0.13659582084855815,0.1355121394832909,0.13433633092264344,0.1330625081084361,0.1316847354248904,0.13019709981032204,0.12859379880632907,0.12686924854569562,0.12501821517563347,0.12303597378194919,0.12091849952515862,0.1186626964177006,0.11626666994571765,0.11373005052973632,0.1110543755454851,0.10824353813806734,0.10530431108914298,0.10224695306806417,0.09908590192093085,0.0958405539246453,0.09253611709519935,0.08920450759050073,0.08588522669177004,0.08262610666708184,0.07948374286688302,0.07652333819167405,0.07381759104495425,0.07144420369503071,0.06948165669085701,0.06800318930038847,0.06706949746030556,0.06672138914975678,0.06697416297172167,0.0678153544665,0.06920657596340295,0.07108886188840026,0.07338993767330171,0.07603161757142554,0.0789360116063626,0.0820299516529236,0.08524764809173134,0.08853191440158638,0.09183438612100561,0.09511511494187379,0.09834182467790113,0.10148902233500998],[0.139719321445729,0.1388939357993393,0.1379925036944878,0.13700919805346137,0.13593792227534313,0.13477232802883407,0.1335058404832961,0.13213169246797624,0.13064296933093103,0.12903266661061588,0.12729376304892473,0.12541931198284212,0.12340255477587928,0.12123706071924306,0.11891689878300926,0.11643684777535668,0.11379265292962948,0.11098133875166447,0.10800159019802866,0.10485421699115169,0.10154271915143284,0.09807397558988448,0.09445908158684864,0.0907143644231236,0.08686260755478678,0.0829345087505466,0.07897037899898492,0.07502204266523724,0.07115480125884467,0.06744913770424461,0.06400152744063875,0.06092328740717769,0.05833597090071339,0.05636182016412985,0.05510891145940117,0.05465329064146447,0.0550235952834141,0.05619462324258558,0.058092950425446634,0.06061189655346245,0.06362946917276542,0.0670235912366178,0.07068206263662724,0.07450747603995919,0.07841854493810226,0.08234936399470673,0.08624771068640795,0.09007305389714435,0.09379461299009077,0.09738961635407753],[0.13930136528072276,0.1384249861797976,0.13746735812571537,0.13642219085999902,0.1352828792862122,0.13404251412214122,0.13269389850574995,0.13122957176482297,0.1296418418001392,0.12792282782876402,0.1260645156035639,0.12405882768863019,0.12189771195660211,0.11957325222206219,0.11707780588914123,0.11440417474657975,0.11154581669592123,0.10849710839937414,0.10525367179996173,0.10181278150999286,0.0981738756342777,0.09433920033433839,0.0903146292468591,0.0861107139366931,0.08174404229847917,0.07723900936295154,0.07263013858638949,0.06796512428453189,0.06330877239074377,0.0587479277687363,0.05439712630364884,0.05040376903803557,0.04694962711312986,0.04424245834574131,0.042489755382793336,0.04185247656184117,0.04239437155289964,0.044058151781865784,0.046686760245899774,0.050073422429800236,0.05400897240330555,0.0583094700225493,0.06282546857300171,0.0674408726280053,0.07206781829757379,0.07664094549530308,0.08111235986757416,0.08544758555321573,0.08962243310841927,0.09362060719214965],[0.1388800593191698,0.13795651087469288,0.13694741874288532,0.13584618210712587,0.1346458618979889,0.13333918691305577,0.13191856456469403,0.13037609713789675,0.12870360460896693,0.12689265528547933,0.12493460579040447,0.12282065224462037,0.12054189492431844,0.1180894192139032,0.115454396384983,0.11262820867203525,0.10960260438044467,0.10636989049663226,0.10292317269447784,0.09925665609511107,0.0953660251953099,0.09124892894177163,0.0869056085054387,0.08233972346087166,0.07755946120380876,0.07257906220820216,0.06742097347891127,0.06211897707881787,0.05672286610054605,0.05130560233326128,0.04597439124976741,0.04088746295354369,0.03627706979655069,0.03247134990181863,0.02988416264699902,0.02891289071568305,0.029738277070202945,0.03220046770466773,0.03590876871351437,0.04044451232735814,0.045471868704886426,0.05075236860891002,0.056123770031638896,0.06147660583498668,0.06673683612186239,0.07185434291150587,0.07679547970790918,0.0815382002119216,0.08606879844430701,0.09037966598573005],[0.13846126934695568,0.13749425958830264,0.136438257763307,0.13528650372209278,0.13403190027062298,0.13266701847160003,0.1311841067430387,0.12957510436228267,0.1278316600840306,0.12594515670567896,0.12390674256849563,0.12170737117717395,0.1193378503642969,0.11678890273517409,0.11405123952336116,0.11111565049811035,0.10797311323699318,0.10461492597907404,0.1010328695160607,0.09721940533994602,0.09316791984693516,0.08887302831912904,0.08433095859302839,0.07954004447675866,0.07450137632684074,0.06921968712663575,0.0637046101013347,0.05797255686950652,0.05204969824660995,0.04597703858641966,0.03981974993124118,0.03368578369190548,0.027765771785142127,0.022420982281511875,0.018348887572826426,0.01664803119365208,0.018043283592643518,0.021915798213037158,0.02714664954752809,0.032994497014018596,0.03907374778847204,0.04518281341779487,0.051209077366028775,0.057085621404193244,0.06277111959811578,0.06823980134475063,0.07347601449352638,0.07847103966504006,0.08322108764240646,0.08772596283196817],[0.13804677005633167,0.13703919258886546,0.13593982234596053,0.13474186170782174,0.13343819897296477,0.13202141653434116,0.1304838026094991,0.12881736695165452,0.12701386102143805,0.1250648031658621,0.12296150943564925,0.1206951307790734,0.11825669748528184,0.1156371719188637,0.11282751079732929,0.10981873852214517,0.10660203339151407,0.10316882891077644,0.09951093288976495,0.09562066759949574,0.09149103499361923,0.08711591195718758,0.08249028187009297,0.0776105107512191,0.0724746794691882,0.06708298920915026,0.0614382683141647,0.055546631171205355,0.04941839002633335,0.04306944252240752,0.0365236865587934,0.029818027690381367,0.023015270786448824,0.01624765008934019,0.009928515557026795,0.0061501131006843355,0.009122575818946078,0.015267288695398451,0.021973887005656674,0.02873425806377384,0.035398562009658886,0.04189981092766017,0.04820049881006271,0.05427742440095979,0.06011594118057609,0.06570722193602047,0.0710466974147494,0.07613303506696056,0.08096740634181229,0.08555293005831188],[0.13763640967613197,0.13658998206253578,0.13544932543932933,0.13420767763276026,0.13285799998443695,0.13139299116420236,0.12980510474910656,0.12808657087943454,0.1262294223189126,0.1242255252708414,0.12206661533923191,0.11974433907917383,0.11725030166023964,0.11457612127847332,0.11171349110541405,0.10865424976672682,0.10539046160868032,0.10191450834777173,0.09821919411487617,0.09429786640376607,0.0901445560108009,0.08575413969394738,0.08112252995861893,0.0762468970576872,0.07112592893789481,0.0657601354798066,0.06015220411560604,0.0543074153505976,0.04823413065322744,0.04194437699825596,0.03545458926167342,0.02878669652516272,0.021970232706097343,0.015048733508794149,0.008116236403289056,0.0021854416579082203,0.006669016105659172,0.013542694573423546,0.020430557234259905,0.02720886502884385,0.03383109570054922,0.04026815986036737,0.04649960048134898,0.052510914553541156,0.058292219990699286,0.0638373524737746,0.06914315769678261,0.07420890714616132,0.07903581082200989,0.08362661327263],[0.1372305577586798,0.1361458824761411,0.13496461321734915,0.13368004123501767,0.13228522484552704,0.13077301041414183,0.12913605759427735,0.12736686903847075,0.12545782477198572,0.1234012213931813,0.12118931624180673,0.1188143766631057,0.1162687345001437,0.11354484598060474,0.11063535724258527,0.10753317588690664,0.10423154917710557,0.1007241498656163,0.09700517114722353,0.09306943298015712,0.08891250303615314,0.08453083692830694,0.07992194423945058,0.07508458942724512,0.07001904027371511,0.06472738193244298,0.059213923551878926,0.053485741234419536,0.04755343709152214,0.04143228157756792,0.03514414555780047,0.02872137601122593,0.022216532856847392,0.015734854212683842,0.009592380999074697,0.005482239415366806,0.007918358859637665,0.013733249001869634,0.02010509137236442,0.02653604841553831,0.03288928998436195,0.03910516502510113,0.045150576862147615,0.051005138501300874,0.05665595752473981,0.06209510802467727,0.06731815697742212,0.07232320073504225,0.07711019618019758,0.08168048472304139],[0.13683236073344585,0.13570939570951707,0.13448731425360025,0.133159431618683,0.13171887191662981,0.13015859684860068,0.1284714393863843,0.12665014255565202,0.12468740339563149,0.1225759220784931,0.12030845606684529,0.11787787907214126,0.11527724445584606,0.11249985259815094,0.10953932165999256,0.10638966110448558,0.10304534735406291,0.09950140108260529,0.09575346593637714,0.09179788902304768,0.08763180441018253,0.08325322227377083,0.07866112842313153,0.07385560196641923,0.06883796327733842,0.06361097088196867,0.05817909581795869,0.05254891867519286,0.046729726253993756,0.04073445520063306,0.03458131324617914,0.028296969381807,0.021924266880415797,0.015547110720669109,0.009411149070065034,0.004927956345567241,0.007057148586881157,0.012797968268369368,0.019046685787431825,0.025330302230593828,0.03152844593769089,0.03759099578585947,0.04349151418406964,0.04921461582159638,0.0547511020111904,0.06009556452147932,0.06524501609758895,0.0701980508217874,0.07495432108053057,0.0795142187123318],[0.13644935995340793,0.13528819486458576,0.13402512466364583,0.13265342850597042,0.13116622899376817,0.12955652863989747,0.1278172522340154,0.12594129527413256,0.12392157851381816,0.12175110853285713,0.11942304406403179,0.11693076759869353,0.1142679615485286,0.11142868796268961,0.10840747049522508,0.10519937700101656,0.10180010083265406,0.09820603865301929,0.09441436242503934,0.09042308327254339,0.08623110523831132,0.08183826775120646,0.07724537705384774,0.07245422918451475,0.06746763064555959,0.06228942794637353,0.05692456410436904,0.0513791892284084,0.04566086389109186,0.0397789092675059,0.03374498191480448,0.027574005959043003,0.02128579106871611,0.014908664656044538,0.008494520158535001,0.002367672665650985,0.004850169876045889,0.011157153347452015,0.017463669851613225,0.023667116808865768,0.029736794824094016,0.03565685963944245,0.04141829202250343,0.047015911486213396,0.052446699580920776,0.05770875219956575,0.0628006429878657,0.06772107849319535,0.07246875716775257,0.07704236255923083],[0.13609416584659098,0.1348959430554616,0.13359279893482506,0.13217790634501153,0.1306443057935618,0.12898494914648798,0.12719275046084436,0.12526064423379324,0.12318165124789111,0.1209489520397141,0.1185559678228927,0.11599644845089252,0.11326456670373095,0.11035501782219923,0.10726312279204274,0.10398493340364647,0.1005173365936373,0.09685815504166324,0.09300624049797829,0.0889615559375319,0.08472524250219263,0.08029966749903725,0.07568845075582836,0.07089646881042976,0.06592984032903847,0.0607959026934959,0.05550320026119797,0.05006152186709717,0.04448205402596942,0.0387777707858939,0.032964303333696834,0.027061871160029626,0.02110003714093065,0.015132403680188177,0.009303656285266599,0.004432411078830727,0.005341112521753999,0.010576848103299421,0.016338621640834536,0.022138737289314554,0.027879430317854264,0.033526975529237946,0.03906619450095093,0.04448883345028409,0.049789307232851465,0.0549628375346434,0.06000463143409104,0.06490959690970138,0.06967235156033788,0.07428738401302563],[0.1357840718874304,0.13455187346982622,0.13321169533853008,0.13175654433440423,0.13017930753570847,0.12847280212797538,0.12662983374044365,0.12464326377392004,0.12250608615965537,0.12021151386705234,0.11775307531198756,0.1151247205979555,0.11232093723966262,0.10933687466256777,0.10616847633278849,0.1028126178419465,0.09926724864799061,0.0955315344622292,0.09160599649661517,0.08749264299442189,0.08319508775773277,0.0787186499297445,0.07407042938903394,0.06925935328182792,0.06429619234949495,0.05919355239157774,0.05396585942328129,0.04862938288090243,0.043202393094137835,0.03770566095863272,0.03216377494117291,0.026608482498586758,0.02108762249760675,0.015692445154701726,0.010661363735655434,0.006864875229100251,0.006790967767584652,0.010463338339312605,0.015348841848311066,0.02055504492805502,0.02584918565425507,0.031151946654515997,0.03642848553667042,0.04165924903237452,0.04683014776931868,0.05192881596838431,0.056943213254526164,0.06186124836184451,0.06667086338034203,0.0713603065556383],[0.1355396781872168,0.13427921418922345,0.13290797727397557,0.13141877743037586,0.12980430667202805,0.128057193349494,0.12617006614114754,0.1241356284985476,0.12194674428012353,0.11959653523302921,0.1170784908680905,0.1143865911055072,0.11151544183563179,0.10846042322228364,0.10521785015513233,0.10178514370716096,0.09816101174393321,0.09434563592916131,0.09034086124026315,0.08615038271428985,0.08177992246746069,0.07723738808383848,0.07253300133984292,0.06767938417521724,0.06269158742799837,0.05758704840005987,0.05238546852909101,0.04710861813744378,0.04178011438473501,0.0364253121199115,0.031071676987886584,0.025750622284170042,0.020503660925505405,0.0154026205151927,0.01062572603939687,0.006807006616588824,0.006028804898701357,0.009046137958433762,0.013487594082378986,0.018331158812607273,0.023321939915293466,0.02838023483414786,0.033472240230706274,0.03857720863696356,0.04367739603304575,0.04875494177263415,0.05379123514502249,0.0587672099482448,0.06366393368155128,0.06846321808874795],[0.13538274853436147,0.13410271557941061,0.13270976649865732,0.1311965267209982,0.12955549779771466,0.12777911413340087,0.12585981024792098,0.12379009954256827,0.12156266553844047,0.11917046652265163,0.11660685446879246,0.11386570897949126,0.11094158681457127,0.10782988729662912,0.10452703349855595,0.10103066857770548,0.09733986588059378,0.09345535043803148,0.08937972812255837,0.08511771694772013,0.0806763726279413,0.07606529744604681,0.07129681754297233,0.06638610882928939,0.06135124580616163,0.05621314093499279,0.050995335698515665,0.04572360041090786,0.04042530343840175,0.03512853409823747,0.02986103765013885,0.024649231380957613,0.01951820970669738,0.014495990709457555,0.009637150074995531,0.00518163208769162,0.0031718129966901995,0.006416557774655943,0.010942108856309205,0.01569321860842868,0.020547868299230103,0.025482850047717488,0.030487605084358813,0.03554903697177443,0.04064909277564217,0.045765586651072915,0.05087380359830608,0.05594808781227131,0.06096315684578438,0.06589508592620102],[0.13533364076035026,0.13404567026708747,0.1326436930967559,0.13112021275375435,0.12946760041581315,0.12767815229191964,0.12574415792378457,0.12365798051314074,0.12141215037415355,0.11899947260404696,0.11641315002642194,0.1136469223790271,0.11069522257561741,0.10755335064925971,0.10421766565592386,0.1006857953471703,0.09695686276397558,0.09303172800102945,0.08891324216543185,0.08460650890707158,0.08011914670313762,0.07546154217652982,0.07064708091576206,0.06569233729463442,0.06061719836496093,0.055444888666140814,0.050201852383729595,0.044917436342828077,0.039623301676054795,0.0343524741055315,0.029137924822489638,0.02401056316282723,0.01899654164634124,0.014113907882838695,0.00936932463213442,0.004761224622460146,0.0007092202027650617,0.004401586658393946,0.008908563811212767,0.01351089318096421,0.01822891403760018,0.02307298436111175,0.028037666597736908,0.03310518248195469,0.038249538028228176,0.043440083405628126,0.048644284934383615,0.05382975260620072,0.05896564467042325,0.06402358215127026],[0.13540872196639403,0.13412690278891348,0.13273139320002494,0.13121468539524855,0.12956913420413257,0.12778701393575934,0.1258605861990498,0.12378217980401117,0.12154428387395737,0.11913965530138844,0.11656144165355915,0.1138033205676776,0.11085965655634976,0.10772567595450312,0.10439766045672241,0.10087315929035573,0.09715121950694522,0.09323263310398155,0.08912019864659874,0.08481899365885755,0.08033665218247468,0.07568363939911579,0.07087351186059505,0.06592314735742387,0.06085292232974368,0.05568680633953602,0.05045233155974939,0.04518037924806803,0.03990470323634588,0.03466108120140491,0.02948594812141833,0.024414329063239763,0.019476875551694996,0.014695913208816674,0.010081048475760303,0.005629513098670117,0.0014593623407890635,0.003275582990677884,0.007627374392722962,0.012151887430813335,0.01684185859729759,0.021696212184360603,0.026699732088033598,0.03182619453808555,0.03704266595040223,0.04231304433392844,0.047600667839229255,0.0528701203970334,0.058088411821165746,0.06322569249069014]],[],[]]},{"xaxis.title":"C","xaxis2.title":"C","xaxis.range":[-9.0,1.0],"xaxis2.range":[-9.0,1.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"C","method":"update"},{"args":[{"x":[[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528]],"y":[[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.016008390888335885,0.023439195729912127,0.02726732442338283,0.02298240909440644,0.022381745344336092,0.022392820449831125],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,85.25159236537601,1000.0,1000.0,690.261692736928,631.8075276764972,633.152764130528]],"z":[[[0.7825999309160263,0.7791559637444286,0.7755612046875043,0.7718623059270656,0.7681194613695492,0.7644066131624461,0.7608104380917559,0.7574276161041409,0.7543599151104028,0.7517068599663337,0.7495563141810011,0.747974219912496,0.7469957312615803,0.7466203397397345,0.7468126714486056,0.7475086852942592,0.7486252557996147,0.7500706052314632,0.7517536646052168,0.7535914354864253,0.7555142097804044,0.75746892099905,0.7594210280946845,0.7613552993573088,0.7632757633819205,0.7652049795279001,0.7671826764332843,0.7692637245376436,0.7715153524830306,0.7740134926568263,0.776838154665799,0.7800677853777304,0.7837726879291717,0.7880077426270202,0.7928048920912666,0.7981660958539885,0.8040576776983853,0.810407111757123,0.817103239212519,0.8240006087702131,0.8309280731325142,0.8377010165014922,0.8441357961257306,0.8500643809760314,0.8553469810426312,0.8598807970641205,0.8636038273921565,0.8664937202751449,0.868562639374112,0.8698497356068255],[0.7817688174220705,0.7782057241461113,0.7744806447697367,0.7706410612165414,0.766748773735469,0.7628803037087047,0.7591260543073426,0.7555876707133791,0.7523730363067228,0.7495885447199085,0.7473288699752499,0.7456655163500318,0.7446366951195749,0.7442416681991937,0.7444416533024928,0.7451669430196806,0.7463277306089853,0.7478256201632305,0.7495636863972572,0.7514541816881776,0.7534238687920276,0.7554173697378341,0.7573990108365758,0.7593535729232832,0.7612862289302748,0.7632218195174099,0.7652035030930325,0.7672907266664842,0.7695564020874534,0.7720831428264381,0.77495842692495,0.7782686121491351,0.7820918501154139,0.7864901333330618,0.7915009575264312,0.7971293661524433,0.8033414121551645,0.8100602421476428,0.8171659809060793,0.8245002806159222,0.8318757661406322,0.8390897216570392,0.8459404130457681,0.8522437011584526,0.8578473485602848,0.8626408093918471,0.8665592580684028,0.8695818800491877,0.8717256224752139,0.8730363338288787],[0.7809595144128343,0.7772791216893056,0.7734253528728785,0.7694463935628939,0.7654055076275009,0.7613816503171235,0.7574688295023149,0.7537735987160631,0.7504100163101179,0.747491562326079,0.7451200869541632,0.7433730650724641,0.7422920340495838,0.7418760145764876,0.7420825457501081,0.7428358844870916,0.7440392334487727,0.7455873981971812,0.7473775334997825,0.7493171500711819,0.7513295169961522,0.7533569812376082,0.7553627638079987,0.7573316794519315,0.7592700727381767,0.7612051162986448,0.7631834930538983,0.765269387622809,0.7675416443192519,0.7700899142017588,0.7730096198083531,0.7763956256589524,0.7803346290300396,0.7848964890502776,0.7901249913581903,0.796028876718947,0.8025742887972849,0.8096800253313086,0.8172169878463683,0.8250129027210394,0.832862675497442,0.8405437053169651,0.8478343441806376,0.8545327735361063,0.8604732354480775,0.8655369993992545,0.8696566039575969,0.8728134435521746,0.8750301821362588,0.8763603316854351],[0.7801754532937346,0.7763802104585884,0.7724000881223575,0.7682838457596898,0.7640960556586267,0.7599179368033685,0.7558469400227967,0.7519944149052549,0.7484805901925393,0.7454261935464632,0.7429405890942544,0.7411076379684215,0.7399724915571565,0.7395339190591206,0.73974550029158,0.7405250963860339,0.7417686525495205,0.7433640571836306,0.7452025412987742,0.7471869261091234,0.7492370481104621,0.7512930240240252,0.7533169920420201,0.7552938080866469,0.7572309957643834,0.759158087437542,0.761125361772431,0.763201880368893,0.7654726522397456,0.7680347135683143,0.770991910534398,0.7744482296092119,0.7784996500409744,0.7832247123209598,0.7886743077296253,0.7948615767700359,0.8017531992978844,0.8092636606662457,0.8172541416541543,0.8255373575891497,0.8338888789898399,0.8420642591432365,0.8498199219425555,0.8569346363168473,0.8632279597214771,0.8685725396728675,0.8728985526209049,0.8761904126809928,0.8784775828856587,0.879822324741719],[0.7794200579395778,0.7755130538820211,0.7714096452466597,0.767159035034543,0.7628269397237039,0.7584966500663786,0.7542688589464538,0.7502595407713224,0.7465950156751773,0.7434033468653115,0.740801704882911,0.7388807506077413,0.7376895554273006,0.7372266285877334,0.7374413031707475,0.7382447067783267,0.739525321537402,0.7411640773395527,0.7430463456775569,0.7450703568789949,0.7471525995656207,0.7492310098750778,0.7512666568906263,0.7532444271897942,0.7551730075155945,0.7570842915340767,0.7590321979995924,0.7610907794776937,0.763351420723086,0.7659188770690442,0.7689058960039585,0.7724262166004576,0.7765858733243233,0.7814729638064697,0.7871463843077035,0.7936244756470223,0.8008749959233625,0.8088082261652225,0.8172751490360415,0.8260723310479419,0.8349542609814453,0.8436524931585245,0.8518992960038422,0.859452112354398,0.8661145516301333,0.8717502087378328,0.8762872756429166,0.8797141596747388,0.8820683750890357,0.883422150652264],[0.7786967113067211,0.7746816836386519,0.7704588045834847,0.7660775932193596,0.7616047410584158,0.7571254009998493,0.7527432707000669,0.7485787178578799,0.7447639914999795,0.7414344866001118,0.7387154052177227,0.7367046055733699,0.735455400786928,0.7349660341015262,0.7351813035041613,0.7360053057962123,0.7373189383258266,0.7389962245134446,0.7409168151452203,0.7429744944103815,0.7450825077968906,0.7471766608316394,0.7492169541505926,0.7511882729709662,0.7531004247544766,0.7549876368435512,0.7569074823650737,0.758939089817195,0.7611804052569546,0.7637442187436242,0.7667526499961378,0.770329831905836,0.774592660961951,0.779639728325821,0.7855389221454792,0.7923146914265545,0.7999365249049226,0.8083106947227636,0.8172775415206959,0.8266162982677197,0.8360584882144986,0.8453093037293891,0.8540743934078725,0.8620877588571684,0.869135689446512,0.8750723107333189,0.8798243332383375,0.8833853214045222,0.8858022861686841,0.8871587848239069],[0.7780087204335573,0.7738900559887403,0.7695522780635919,0.7650451007920248,0.7604360212146433,0.7558118324120877,0.7512789679898937,0.746961898641737,0.7429985497212734,0.7395315336205396,0.7366942144222999,0.7345920095373416,0.7332828068537118,0.7327645808253722,0.7329773144017402,0.733817841419814,0.7351594631940086,0.7368694574558137,0.7388219713672922,0.7409065309045615,0.7430332578948619,0.7451358722392035,0.7471732892941103,0.7491303359050786,0.751017868476058,0.7528723885917981,0.7547551051575438,0.7567502751164785,0.7589625615753953,0.7615130811568085,0.7645337839990144,0.7681598426149295,0.7725198511317977,0.7777238894032317,0.7838499148193727,0.7909295086248411,0.7989346676474798,0.8077679559908266,0.8172586781358842,0.8271675100373944,0.837200983641078,0.8470353379168495,0.8563468737233424,0.8648438107975375,0.8722936274221905,0.8785405857412765,0.8835105685277087,0.8872036833866013,0.8896781028157261,0.8910302292659688],[0.7773592804424426,0.7731420062952051,0.7686946520978671,0.7640670158288773,0.7593272349707856,0.7545635146595495,0.7498847309337657,0.7454191133693945,0.7413099184986991,0.7377067338197311,0.7347510890882276,0.7325562588272618,0.7311850421143571,0.7306351463761962,0.7308414825955586,0.7316934875149543,0.7330569950196087,0.734792819306773,0.7367698989214728,0.7388737268076153,0.74101142851141,0.7431146725161654,0.7451412502620245,0.7470758451608153,0.7489302591520908,0.7507431747869953,0.7525793829370463,0.7545282859231277,0.7567013855612352,0.7592283875549642,0.7622515112107856,0.7659176118875843,0.770367839441171,0.7757248127568727,0.7820777276590412,0.7894664461061487,0.797866390993888,0.8071768449930243,0.8172157517807996,0.8277239796115594,0.8383808981793457,0.8488309537827237,0.8587180786439629,0.8677221173151011,0.8755901151402233,0.8821561099967112,0.8873459908397203,0.8911680531820927,0.8936935443087347,0.8950333952207258],[0.7767514382506865,0.7724412026589015,0.7678903285405567,0.763148599295066,0.7582846367789403,0.7533878305168161,0.7485691892892454,0.7439603122344476,0.7397093524137892,0.7359724891237196,0.7328992586570869,0.7306109873978236,0.7291757118442225,0.7285908807444621,0.7287861219752586,0.7296434819655466,0.7310216256468511,0.7327753144786637,0.7347686458479898,0.736883333237745,0.739023633249452,0.74111918054573,0.7431265783898273,0.7450302513103633,0.7468428102477036,0.7486049902977724,0.7503850735473262,0.7522775863570635,0.7544009527141354,0.7568936948137892,0.7599087130442886,0.7636051778472868,0.7681376672621365,0.773642439023616,0.7802211878345604,0.7879233363523127,0.7967288078936637,0.8065341787408211,0.817145800206292,0.8282834705373314,0.8395970803043059,0.850696176186406,0.8611889753460984,0.8707240703148358,0.8790263074241179,0.8859191851906061,0.8913296474587836,0.8952761230067181,0.89784512731153,0.8991639804926567],[0.776188056775596,0.771791099724937,0.7671434651319713,0.7622948384859423,0.7573141829775872,0.7522918517687283,0.7473406700088852,0.7425951837986042,0.7382079284193244,0.7343411457878442,0.7311520207993347,0.7287699701728293,0.7272685609331542,0.7266450015025787,0.7268235067686334,0.7276789340457424,0.7290632738837797,0.7308257733437789,0.7328261174172697,0.7349425108081392,0.7370764600894122,0.7391555617725846,0.7411351381315858,0.7429992076282554,0.7447610200099605,0.7464631989276853,0.7481773890216811,0.7500031789537529,0.7520659563260148,0.7545132462424344,0.7575090072324314,0.7612253363875392,0.765831116681925,0.7714773858195227,0.7782796859635607,0.7862984172666435,0.7955192499535355,0.805836802309128,0.8170457227058172,0.828843485992554,0.8408480434087491,0.8526306475478975,0.8637600928110404,0.8738505243518695,0.8826026638902155,0.8898292160737943,0.8954594833370959,0.8995243215976411,0.9021280228599109,0.9034163427978461],[0.775671780472028,0.7711948938205637,0.7664579170171881,0.761510370784614,0.7564214326209984,0.7512822110645343,0.7462070340040997,0.7413329527716008,0.7368163076381854,0.7328247354148032,0.7295224837998416,0.7270468736416942,0.7254772239063171,0.724810537073267,0.724965621348992,0.7258106024466237,0.7271915027008187,0.7289527085977877,0.7309499664421384,0.733058247409625,0.7351764106931107,0.7372299842347875,0.7391728863151841,0.7409885503057934,0.7426906615121553,0.7443235331704976,0.7459620057979892,0.7477106267727611,0.7497017433414447,0.7520920230921426,0.7550568163635698,0.7587817268595053,0.7634508113714482,0.7692310589698841,0.7762532897338572,0.7845904376583065,0.794235353463178,0.805081646041978,0.8169123038474987,0.8294012603256632,0.84213193091456,0.8546335729903675,0.8664314501939345,0.8771017067650767,0.886318837150212,0.8938845755874691,0.8997321884434839,0.9039076556892268,0.9065359066802,0.9077833709479738],[0.7752050030641993,0.7706554806455965,0.7658371810720691,0.7607994101803887,0.7556114503302318,0.7503649736232054,0.7451755078668066,0.7401821632167636,0.7355444668201967,0.7314346663197101,0.7280232475536397,0.725454944363507,0.7238149128150924,0.7231000110047973,0.7232238665578342,0.724048648910007,0.7254153258236159,0.7271641687534522,0.7291474843299143,0.7312372779658103,0.7333298416445684,0.7353485758581464,0.7372458416945555,0.739004277903876,0.7406377709099592,0.7421920912803088,0.7437450715797658,0.7454060718298653,0.7473143467110946,0.7496357933848928,0.7525574353760167,0.7562789192525063,0.761000322293318,0.766905772391219,0.7741428697856906,0.7827987774626655,0.792875160579843,0.8042657957876215,0.8167422458481236,0.8299537536920071,0.8434464791858911,0.8567036592122391,0.8692024761753202,0.8804771168676878,0.8901735485837119,0.8980824567913671,0.9041430326437728,0.9084195418574069,0.9110608045320434,0.9122563562794004],[0.7747898383216179,0.7701754167436399,0.7652843448237983,0.7601656791596841,0.754888714977716,0.7495455142848727,0.7442525181773246,0.7391504567926845,0.7344014087484856,0.7301813679668867,0.7266660151460729,0.7240066246332937,0.7222940323392208,0.7215250621318439,0.7216087281505056,0.7224023773884911,0.723743012880482,0.725467595737228,0.7274254977831653,0.7294860094828601,0.731542909803643,0.7335173843680143,0.7353600555530589,0.7370525303381545,0.7386086338259187,0.7400753312375613,0.7415332081042583,0.7430962487976509,0.7449105128775609,0.7471511564354905,0.7500170962138505,0.7537225010705143,0.7584842767099311,0.7645048756549366,0.7719502377390981,0.780923583574284,0.7914372374008093,0.8033865782987142,0.816532211507985,0.8304976509438489,0.8447889784053702,0.8588390463798047,0.8720719180616581,0.8839754128198077,0.8941644505072,0.902418710944955,0.9086856883213926,0.9130516300308671,0.9156929349580158,0.916824867449318],[0.7744280946787895,0.7697568859293007,0.7648020417135061,0.7596123485981022,0.75425703819749,0.7488284059961017,0.7434435375932246,0.738244359311351,0.7333948682393471,0.7290739013124299,0.7254611307120157,0.7227130829853602,0.7209257101642216,0.7200960022707911,0.7201294228005082,0.7208799747547893,0.7221819051351508,0.7238696947411745,0.7257902764794464,0.7278104548218199,0.7298215239327298,0.7317423411186508,0.7335215840515075,0.7351395676350103,0.7366097697284899,0.7379800611394304,0.7393335090106036,0.7407884928172211,0.7424977228728754,0.7446455811974738,0.747443027499101,0.7511191616504935,0.7559084684070565,0.7620328876923695,0.7696782957594386,0.7789659218703349,0.7899208106251536,0.8024416641635073,0.8162788799942945,0.8310293662662375,0.8461562317382864,0.8610372322850794,0.8750377392069488,0.8875942845898106,0.8982879734658095,0.9068876712342497,0.9133520413805102,0.9177936206699375,0.9204205526795433,0.9214766325582623],[0.7741212544091469,0.7694016717297552,0.7643924143033781,0.7591419881227505,0.7537194965968279,0.7482173259238347,0.7427529527558381,0.7374690918284916,0.7325310385199496,0.7281195648602021,0.7244170535895869,0.7215836455099796,0.7197192308903195,0.7188213313600811,0.7187935513554623,0.7194882751875131,0.7207382559027572,0.7223763250046203,0.724247457057563,0.7262161784702268,0.728171304588109,0.730029229995441,0.7317364629025616,0.7332717486156519,0.7346479141132644,0.7359134254951245,0.7371535319466597,0.738490740180098,0.7400842053654975,0.7421274363304746,0.7448435067192231,0.7484767711693475,0.7532799664174222,0.7594956343985753,0.7673311963978005,0.7769279455432166,0.788325924368381,0.8014291908356059,0.8159790181800427,0.8315450554750599,0.8475445133486673,0.8632949879930969,0.8780970031094153,0.8913303111536917,0.9025391572696476,0.9114819618467477,0.9181319918640481,0.9226330785217357,0.925229796931462,0.9261974335273117],[0.773870457937605,0.7691111367203927,0.7640570867792117,0.7587565290671752,0.7532783810912964,0.7477149848811532,0.7421839637650132,0.7368284235318137,0.7318143489843507,0.7273235481923356,0.723539820629852,0.7206251145690216,0.7186813765114043,0.7177072688577827,0.7176068046213292,0.7182325742864999,0.7194171101626731,0.7209924197726812,0.7228019882153365,0.7247082571524692,0.7265975539386906,0.7283836623102236,0.7300106847924324,0.7314555095617049,0.7327299982311284,0.7338828868680425,0.735001284018858,0.7362115205835282,0.7376789398833659,0.7396060096785906,0.7422279020789718,0.7458044510582855,0.7506072188160634,0.7569003870458105,0.7649145105907315,0.7748130791935147,0.7866536183936614,0.800347908467873,0.8156295707076155,0.8320406384251651,0.8489495261730572,0.8656082642281441,0.8812457422996078,0.8951787997791789,0.9069114642903274,0.9161922924051124,0.9230132462120008,0.9275552470217873,0.9301045503052826,0.9309710187574726],[0.7736764937183724,0.7688862094011508,0.7637971477516852,0.7584572416184727,0.7529351659967157,0.7473230845710898,0.7417385233062466,0.736324581801008,0.7312473256446319,0.7266887006006664,0.7228326292138485,0.7198410382504384,0.7178157921549626,0.7167574137796788,0.7165727751444693,0.7171165180182123,0.718222235951725,0.7197219421421587,0.7214581006564873,0.7232912574006177,0.7251052366958521,0.7268110582932558,0.728350179767679,0.7296973427944126,0.7308631260457801,0.7318962022831508,0.732885199682425,0.7339599396438807,0.7352916483719563,0.7370915146834053,0.739606700842931,0.7431126320064858,0.7479001473767894,0.7542559974210606,0.7624354006233418,0.7726262172003204,0.784906128493799,0.7991973512774376,0.8152277724345267,0.8325118346334106,0.8503663608383212,0.867972087849054,0.8844788098896776,0.8991336048925361,0.9113965734329632,0.9210072382117722,0.9279811042411207,0.932542868885009,0.9350263152006761,0.9357790413131367],[0.773539793922955,0.7687273789852981,0.7636131439364642,0.7582447270913604,0.7526904994421109,0.7470423053876852,0.741417320511525,0.7359582296125362,0.7308305569209714,0.726215473397984,0.7222957233063412,0.719231441311991,0.7171227815504044,0.7159726604809968,0.7156929181335198,0.7161420840449892,0.7171561156929842,0.7185678809254086,0.7202193040801752,0.7219692312548763,0.7236989727367603,0.725316635403948,0.72676079857008,0.7280037749683732,0.7290545480473428,0.729961393815294,0.7308141101968324,0.7317456503818295,0.7329327732369577,0.7345950811519896,0.7369915207252873,0.7404130952188904,0.7451702280502202,0.7515730244598302,0.7599027935228803,0.7703739336196022,0.783087108910618,0.797978036996286,0.8147712873968337,0.8329542160186649,0.8517894577739471,0.8703804479826933,0.8877897114182078,0.903186923633979,0.9159841531170446,0.9259130073783323,0.9330182453200251,0.9375760202775667,0.9399741167852853,0.940601031166485],[0.773460435987656,0.7686346981728372,0.7635050848246184,0.7581189255115965,0.7525442154201747,0.7468723253575404,0.7412198107012041,0.7357285127358465,0.7305627706231158,0.7259020527307762,0.7219266484102115,0.7187933705721405,0.7165997469854284,0.7153514119702302,0.7149666734453085,0.7153096598540171,0.7162199993375231,0.7175322873646202,0.7190884115472521,0.720745730157733,0.7223830413236132,0.7239054032605459,0.7252482986502689,0.726381344748715,0.7273116315063006,0.728086712798387,0.7287972038403667,0.7295788124795248,0.7306134400854091,0.7321287277825002,0.7343951006987843,0.7377189921345586,0.7424305513860255,0.7488638458806025,0.7573275487377575,0.7680646991920692,0.7812018754021737,0.7966916964850216,0.8142583788315847,0.8333632816034903,0.8532125754712724,0.8728261717828688,0.8911704144366925,0.9073290647861612,0.9206616115596391,0.9308931967785103,0.9381045200361887,0.9426319682554013,0.9449244434378516,0.9454144113501161],[0.7734381498715952,0.7686077936761178,0.7634724579763992,0.7580791379188812,0.7524953665017597,0.7468118685525154,0.7411442879791892,0.7356331707551761,0.7304410088064978,0.7257446468399533,0.7217207439684687,0.7185216474190668,0.7162418826219774,0.7148900052241217,0.7143917226317049,0.7146182073604508,0.715414014413275,0.7166163500360552,0.718067589609653,0.719623835955366,0.7211613961163909,0.7225821645550872,0.7238183323373502,0.7248365794176386,0.7256418267294421,0.7262805971520885,0.7268439761944646,0.7274700382630978,0.7283454035320165,0.7297053139423783,0.7318312675323321,0.7350448374621689,0.739695856230854,0.7461427469733846,0.7547226120693215,0.7657090989004705,0.779257665727829,0.7953415346525907,0.8136881150292437,0.8337345600969973,0.854628769044465,0.8753007904437359,0.8946111332023646,0.9115481873423618,0.9254138226976091,0.9359285399554569,0.9432167560146802,0.9476850639635986,0.9498512379740622,0.9501945690824497],[0.7734723306869475,0.7686458839760484,0.7635142541204066,0.7581240620783276,0.7525422750528251,0.7468587792714871,0.7411879940064197,0.7356686990016452,0.730460872971041,0.725737861213752,0.7216716951828559,0.7184095190833458,0.7160428197935041,0.7145832163695426,0.7139643307575013,0.71406549223842,0.714737322329758,0.7158205021734338,0.71715843079808,0.7186062068371426,0.7200376895032394,0.7213515209040746,0.7224764364039519,0.7233759698525475,0.7240526288832559,0.7245516214162021,0.7249641699776,0.725430324590972,0.7261409746924467,0.7273384684212735,0.7293148744675026,0.7324064702089081,0.7369825293656692,0.7434259773345948,0.7521031456912528,0.7633200408461567,0.7772639117593956,0.7939325222238541,0.8130606156760467,0.8340637474361571,0.8560303848166195,0.8777943971365219,0.8981000859632833,0.9158300046335291,0.9302228262827542,0.9409966517453515,0.9483285895811427,0.9527066874686827,0.9547259554549498,0.9549149938847685],[0.7735620561935729,0.7687478035323339,0.7636290008505229,0.758251839683534,0.7526825998320117,0.7470101167412799,0.7413472537614713,0.7358305444995439,0.7306168069102793,0.7258750973462416,0.7217720438276733,0.7184491989329274,0.7159951706680261,0.7144247519680756,0.7136797202203607,0.7136483511381083,0.7141883067059971,0.7151445533745762,0.7163620436352685,0.7176951351284324,0.7190153041812277,0.7202178822149996,0.7212280220601017,0.7220059432429421,0.7225515349858184,0.7229084392168827,0.7231677041327049,0.7234709701341953,0.7240129293533596,0.7250424932654423,0.7268617087509497,0.7298209774388104,0.7343085633016343,0.7407317650813697,0.7494866217921579,0.760912943991397,0.7752325139724527,0.7924717153561194,0.8123773426438163,0.8343468874935706,0.8574090786471282,0.8802955001063478,0.901623222794895,0.9201574497806179,0.9350675011570664,0.9460717765963076,0.9534103388029034,0.9576652640631893,0.9595177059045323,0.9595474951474197],[0.7737061085095965,0.7689120324658518,0.763814803411347,0.7584601126904693,0.7529134142003125,0.7472622641805664,0.7416176279844857,0.7361133183508335,0.7309023875185457,0.726148930941245,0.7220136255370321,0.7186323095807811,0.7160909760965715,0.7144076839085142,0.7135324360049947,0.7133629710243485,0.7137647784118154,0.714587836465479,0.7156791544051346,0.7168926131723987,0.7180973894491387,0.7191854778465383,0.7200783642487208,0.7207328328751887,0.7211459957398352,0.7213597180640064,0.7214645921511617,0.7216034779201962,0.7219743962957721,0.722832241360588,0.7244883652936492,0.7273065758737447,0.7316934643552686,0.7380802770805751,0.7468928650567478,0.7585058885735674,0.7731781045614777,0.7909685962785713,0.8116414375197298,0.8345806050522815,0.8587558681615037,0.882790876451882,0.9051639229988989,0.9245102985014493,0.9399232116701565,0.9511245505563422,0.9584289382225943,0.9625263763859546,0.9641935025500965,0.9640625111651261],[0.7739029992844799,0.7691367305861854,0.7640693908659104,0.7587460861651657,0.7532312918756201,0.7476110458334412,0.7419940722129353,0.7365110089109779,0.7313106012504538,0.7265514462246501,0.7223879301396924,0.7189502413056692,0.7163220689513383,0.7145248157677198,0.7135166775004924,0.7132051598185378,0.7134641830422105,0.7141493601538226,0.715110214492678,0.7162004031225606,0.7172868993448426,0.7182583676213483,0.7190325890110922,0.7195628443196622,0.7198433619896973,0.7199140665948763,0.7198648499469312,0.7198394434720518,0.7200387258535061,0.7207229671764468,0.7222120845631301,0.724882447222308,0.7291581035132189,0.7354935132031767,0.7443440270971414,0.7561197088787799,0.7711182797368974,0.7894354225986724,0.8108581050090815,0.8347624004305323,0.8600612318988307,0.8852654353415114,0.9087026630416285,0.92886474635771,0.9447614289825681,0.9561217909209058,0.9633479614013036,0.967253001553505,0.9687186378069176,0.9684295198526276],[0.7741509975154313,0.7694197745574396,0.7643901658526633,0.7591065949618925,0.7536323961988919,0.7480518459277447,0.7424710935286964,0.7370171834948664,0.7318340920473634,0.7270745173970111,0.7228863906219726,0.7193944365616058,0.7166803634159817,0.7147689813309264,0.713626584616282,0.713170593706691,0.7132837988836868,0.7138279587863889,0.7146555071591668,0.7156201063106099,0.7165866295770551,0.7174404506229797,0.7180956576499598,0.7185020174082984,0.7186508257348807,0.7185799546322724,0.7183783939690861,0.7181904294019478,0.7182193395032908,0.718730151018053,0.7200505539532099,0.7225685243580051,0.7267245036264484,0.7329951228264844,0.7418644744096146,0.7537780038637628,0.7690737748959012,0.7878875652261113,0.8100350359541133,0.8348910141918638,0.8613152714667778,0.8877021038435345,0.9122166593794881,0.9331929400096317,0.9495493321795091,0.9610263328753492,0.9681277641692045,0.9718059072731595,0.9730572094802962,0.9726175575209784],[0.7744481591624361,0.7697587969802443,0.7647742561572345,0.7595381716542602,0.7541125691913464,0.7485797242935467,0.7430428979247321,0.7376251701232277,0.732465373327446,0.7277100362914873,0.723500608314998,0.7199566098010327,0.71715807924842,0.715133280261987,0.7138564739580942,0.7132550320868261,0.713220916257011,0.7136224317165725,0.7143152480163847,0.7151532279130458,0.7159992501547723,0.7167354696742617,0.7172723464456701,0.7175561834951572,0.7175753558195522,0.717365626708586,0.7170149306488119,0.7166678278941497,0.7165295620888572,0.7168692982300514,0.7180216733189368,0.7203852272167188,0.7244155582878263,0.7306101330578771,0.7394805709448439,0.7515070373628331,0.7670685485287339,0.7863438045701572,0.8091828551150471,0.8349668672108941,0.8625079556301546,0.8900817543890752,0.9156794959919345,0.9374624669828155,0.9542493996355316,0.9657969395113047,0.9727257889251558,0.9761442447872463,0.9771728175492501,0.9765958454270423],[0.7747923577297153,0.7701512262118976,0.7652185664348329,0.7600371133873698,0.7546674171973562,0.7491895244132124,0.743703523179915,0.738328214265178,0.7331970014774369,0.7284500891907036,0.7242225218039007,0.7206289104807262,0.7177479086441045,0.7156112567964344,0.71420102516692,0.7134544953852742,0.7132729918159961,0.7135316661775536,0.7140896740725542,0.7148012328571626,0.715527330687838,0.7161470094516911,0.7165672207800762,0.716730917649567,0.7166236286406872,0.7162790100136729,0.7157838387025941,0.7152827131172741,0.714982439148848,0.7151557160384321,0.7161432870870635,0.7183531495571849,0.722254680459258,0.7283645807579398,0.7372203375492596,0.749335497142196,0.7651297325333315,0.7848265415010162,0.8083155658342778,0.8349925744712692,0.8636294669143856,0.8923832002486171,0.9190607550034386,0.9416358174851773,0.9588190104268107,0.9703883207724352,0.9770970775846335,0.9802263780297451,0.9810294460227273,0.9803345133486924],[0.7751813150277268,0.7705943258407871,0.7657198286022541,0.7605995456647621,0.7552923905435667,0.7498759708047873,0.7444469540201935,0.7391196083186486,0.7340217113876442,0.72928708737773,0.7250445263951817,0.7214040359558438,0.718443132079049,0.7161970269551378,0.7146554194899356,0.7137654037913111,0.7134377735983802,0.7135547388969072,0.7139791169062789,0.7145655892185216,0.7151733554969393,0.7156784863363643,0.7159846026963219,0.7160314856409977,0.7158019544693688,0.7153276180408267,0.714694046238135,0.7140456862095889,0.7135905427072612,0.7136042720357348,0.714432887295295,0.7164927004875431,0.7202653825729523,0.726285044673133,0.735112974058054,0.7472940820585373,0.7632873992881707,0.7833618637066084,0.8074509448587932,0.8349735181371734,0.8646706700123469,0.8945832940686853,0.9223256818064571,0.9456698474898686,0.9632100911420601,0.974751308679557,0.9811950460191831,0.9840109851362668,0.9845925328620474,0.9838053941684972],[0.7756126314039138,0.7710852328640725,0.7662746496523576,0.7612214814882771,0.7559828553262368,0.7506337537401615,0.745267217979871,0.7399927936365682,0.7349325163972008,0.7302138565051088,0.7259595502472732,0.7222752999987357,0.71923768842822,0.7168853589802568,0.7152154332489389,0.7141846765821793,0.7137133942368217,0.7136909928186945,0.7139840561737503,0.7144477957125723,0.7149397259136911,0.7153331283376744,0.7155285311735591,0.7154627858361469,0.7151162002554601,0.7145184515195346,0.7137539050118211,0.7129667160512441,0.712365769745358,0.7122291396484697,0.7129072939796683,0.7148237077989898,0.7184707943809651,0.7243980800082789,0.7331882363858759,0.7454148905935238,0.7615740915043505,0.781979390639651,0.80661081461032,0.8349184435973855,0.8656237139172798,0.8966571735512208,0.9254349355584256,0.9495152984536435,0.9673688687579399,0.9788332511079278,0.9849725725205444,0.9874584565688941,0.9878302115679206,0.9869828424555569],[0.7760838148252795,0.7716209937765963,0.7668795559065364,0.7618988746942609,0.7567341561054826,0.7514576002865521,0.7461584616927069,0.7409414363374398,0.735922776004162,0.7312236898837883,0.7269610926351477,0.7232366619153794,0.720126203753527,0.717671710806031,0.7158774887303316,0.714709792450197,0.7140984307598813,0.7139400861378487,0.7141051501926661,0.7144493902346623,0.7148287474667183,0.7151139437588925,0.7152027147289485,0.7150292864397431,0.7145717100757252,0.7138578985201917,0.7129710645427384,0.7120549795370115,0.7113191383478965,0.7110435371791739,0.7115823213833473,0.7133649934794322,0.7168931300705182,0.7227295655256591,0.7314756710794219,0.7437305938442484,0.7600240628442592,0.7807118041174301,0.8058210864104088,0.8348400074048654,0.8664827610225255,0.8985787053475267,0.9283445046930298,0.9531164711786285,0.9712358304119009,0.9825787048968112,0.988383440612191,0.9905325877087305,0.9907146782613611,0.989844502801595],[0.77659230830422,0.7721985979518557,0.767531032992014,0.7626276667446884,0.7575416688941157,0.7523423314908446,0.7471150083387711,0.7419594790704205,0.7369862351764023,0.732310370636023,0.7280432293444923,0.7242827206918409,0.7211039824661523,0.7185522275413166,0.716638664505189,0.7153388113757063,0.7145919299261917,0.7143020113761707,0.7143432407332069,0.7145719367440397,0.7148426000528529,0.7150236777204779,0.7150104763809969,0.7147349588671636,0.7141732246789193,0.7133516358782782,0.712352349074133,0.711318705454856,0.710460587142826,0.7100594680880297,0.7104724403338201,0.7121339350422816,0.715553121732638,0.7213039823827266,0.7300037235418235,0.7422733932804059,0.758672190095713,0.7795939627147654,0.8051114278803245,0.8347551539138552,0.8672447981524283,0.9003211778242743,0.9310059095880325,0.9564112168436573,0.9747460525786221,0.9859305312479038,0.9913841419235041,0.9932025142755021,0.9932235957684614,0.992371920539315],[0.7771355152738038,0.7728150078714293,0.7682255610939053,0.7634038266134441,0.7584008443538468,0.7532829061872415,0.7481313976845871,0.7430411714714629,0.7381170392946064,0.7334681674746762,0.7292005898980767,0.7254086783107898,0.7221669641387749,0.7195237012543076,0.7174966665079388,0.7160703583195157,0.7151933981397531,0.7147770824533282,0.7146993293753982,0.7148169881442454,0.7149832897253199,0.7150647562434882,0.7149546915233764,0.7145832084314321,0.7139248018648487,0.7130045342965086,0.7119036405658039,0.7107650263239229,0.7097987840722193,0.7092874709643324,0.7095904486402569,0.7111460291689634,0.71446944162716,0.7201436536467636,0.7287987528399332,0.7410737890227238,0.7575525465766154,0.7786615069250971,0.8045143669319845,0.834685124218976,0.8679104146825072,0.901858274690688,0.9333668777426146,0.9593315059146209,0.9778301526968352,0.988831520614119,0.9939359724940503,0.9954447545433729,0.9953413903088559,0.9945508503962797],[0.7777108226335012,0.7734671859281248,0.7689596452739409,0.7642233837407978,0.7593072415404207,0.7542744524046622,0.7492024106291635,0.7441810823579932,0.7393097288012118,0.7346918087309897,0.7304283112101804,0.7266102763599083,0.7233116491452837,0.7205834949181383,0.7184497604967012,0.7169035684768745,0.7159027547827235,0.7153658876621202,0.7151745228933918,0.7151860232616726,0.715252581465939,0.7152392183532227,0.7150377198666178,0.7145768039460458,0.7138297396915927,0.7128205696260902,0.7116297709798483,0.7103998426201419,0.7093409506905474,0.7087363880374402,0.708947162308595,0.7104144762635891,0.713658140146068,0.7192679825655396,0.7278840039616434,0.7401592169881488,0.7566966756257278,0.7779489049723542,0.8040636200679653,0.8346548062401268,0.868484316993933,0.9031653049267646,0.9353727704817351,0.961804973415438,0.9804162407908773,0.9912266925715449,0.9960072287452311,0.9972450875325173,0.9970602278916066,0.996371082576478],[0.7783156212958525,0.774152117682944,0.7697298408595719,0.7650824543045077,0.7602565528695979,0.7553122876972169,0.7503230804548164,0.745374096844274,0.7405592175908389,0.7359764391697865,0.7317219723295187,0.7278837103273943,0.7245349966294133,0.7217294323549104,0.7194966659245615,0.7178379931355117,0.7167202473483434,0.7160692061842551,0.7157699451836481,0.7156803567176061,0.7156519133490858,0.7155486376193738,0.7152613332941948,0.7147178082666634,0.71389050471633,0.7128027428864612,0.7115344270718283,0.7102277036969944,0.7090927080453072,0.7084131610107866,0.7085511405917421,0.7099498055008973,0.7131321291962347,0.7186927347127787,0.7272786047723423,0.7395526489650034,0.7561316721118143,0.7774869860095023,0.8037914637177597,0.8346910264629638,0.8689751747569648,0.9042205433378813,0.9369691688925293,0.9637580183693056,0.9824334017704771,0.993066400167799,0.9975751239662961,0.9985997921862766,0.99838037907399,0.9978255826896106],[0.7789473241645226,0.7748668315915583,0.7705327740835405,0.7659772612710614,0.761244621212496,0.7563919299389131,0.7514886931201405,0.7466154015700893,0.7418607590894344,0.737317564089945,0.7330775151293466,0.7292255265359889,0.7258342991432319,0.7229596566435952,0.7206364109854689,0.7188734643829036,0.7176463261148508,0.7168878853245076,0.7164866134501978,0.7163010216826218,0.7161822939699239,0.7159940357079516,0.7156266422168539,0.7150075121867008,0.714108667618062,0.7129530115427064,0.7116200707104051,0.710251709382927,0.7090579497346783,0.708322662423305,0.7084084572690901,0.7097595595304287,0.7129007412218593,0.7184294124556108,0.7269966660444875,0.7392712809994011,0.7558782588242013,0.7773001698864931,0.8037251360007583,0.8348192939975577,0.8693941677859941,0.9050063503816037,0.938106141625995,0.9651212411636404,0.9838173783387045,0.9943102407793912,0.9986268538256213,0.9995154835782707,0.9993095890372973,0.9989087668328548],[0.7796033815616199,0.7756084153291507,0.771365158292682,0.7669041488465193,0.7622674501803551,0.7575091002331482,0.7526947789552756,0.7479004611526472,0.7432099038357081,0.7387109851719915,0.7344911560692037,0.7306325074478213,0.7272070397066892,0.7242724610666542,0.7218681490914478,0.7200099161002799,0.7186814753075799,0.7178226750588653,0.7173252771014095,0.7170486275767927,0.7168441869893439,0.7165757918372635,0.7161340237333729,0.7154463744211987,0.7144848486008457,0.7132722344107698,0.7118878774190287,0.7104734357087625,0.7092387469611434,0.7084675696443253,0.7085225290406449,0.709848056027815,0.7129693917995256,0.718484768465263,0.7270465650393876,0.7393254522837436,0.7559491100745166,0.7774038067561958,0.8038826815283635,0.8350585878951621,0.8697513690009865,0.9055096451468879,0.9387445386477629,0.9658381924186275,0.9845190362032592,0.9949313965600666,0.9991592120886822,1.0000064575036574,0.9998609149855044,0.9996139365538249],[0.7802812941951828,0.776374028931811,0.7722238061459894,0.7678595920473313,0.7633212087359573,0.7586597196075445,0.7539370980509242,0.7492249888121361,0.7446024521890845,0.7401527324528983,0.7359592943899462,0.7321015519452199,0.7286507389594797,0.7256660996244535,0.7231909391653553,0.721247158091784,0.7198259967724101,0.7188740159386849,0.7182862199784548,0.7179231981948646,0.717637389121711,0.7172935533807326,0.7167830555237655,0.7160339706080171,0.7150186749105222,0.7137601322970271,0.7123376953703939,0.7108928875061555,0.7096352893382631,0.7088482870322033,0.7088940095749974,0.7102162397840386,0.7133393685530862,0.7188604975520159,0.7274304835624168,0.7397179294154232,0.7563476938942838,0.7778021951856969,0.8042693296330526,0.8354148406696847,0.8700492936406644,0.9057217381088615,0.9388634074991353,0.9658783737886362,0.9845148706635349,0.9949203416928198,0.9991765829748152,1.0000885495347476,1.000047995422605,0.999930800881024],[0.7809786238155454,0.7771609150382196,0.7731056382879375,0.7688402021632379,0.7644022312831171,0.7598399011122763,0.755211621490478,0.750584913893493,0.7460344055269146,0.741638996624534,0.7374784221928412,0.733629557937153,0.7301628022234046,0.7271385885985695,0.72460349748733,0.722584600700584,0.7210797411394538,0.7200417764723411,0.7193690318733377,0.7189240007935026,0.7185609105992381,0.7181461540193474,0.7175724597920548,0.7167689542713604,0.715708752597394,0.7144152661017504,0.7129680264838638,0.7115084797536224,0.7102458639144388,0.7094629198227397,0.7095207547112015,0.7108616342229005,0.7140077613830618,0.7195531333055903,0.7281442499116119,0.7404436549484941,0.7570678498753419,0.778487815700825,0.8048759241850149,0.8358771339764588,0.870277796365847,0.9056384686718082,0.938465075963926,0.9652500566178355,0.98381442719005,0.9942863258781025,0.9986880949161955,0.9997707394085233,0.9998754599499249,0.9998468928612104],[0.7816930017519327,0.7779664065583529,0.7740076890171372,0.7698427288938092,0.76550701434812,0.7610459388301378,0.7565145103734776,0.7519763487160073,0.7475019189455415,0.7431660655165551,0.7390450416707951,0.7352133149671535,0.7317403780803149,0.7286875160271534,0.7261039394508986,0.7240209325433127,0.7224417802927116,0.7213249397721839,0.7205723664354664,0.7200493829393197,0.7196128694771431,0.7191315465065728,0.7185000616126926,0.7176490324838636,0.7165526543117824,0.7152350336344571,0.7137760306024636,0.7123170485740323,0.7110668734279496,0.7103073010908221,0.7103978608114632,0.7117783955505524,0.7149675394581008,0.7205541593301179,0.7291775034601622,0.741489999139038,0.7580941928937057,0.7794420260512235,0.805680267932525,0.8364208177127979,0.8704185164328985,0.905261361374663,0.937574148363217,0.963996144983835,0.9824576126084411,0.9930556481061042,0.9977055095325729,0.9990507103653984,0.9993312964263898,0.9993553048201373],[0.7824221355488601,0.7787879321184518,0.7749271094768218,0.7708640599146862,0.7666322108886326,0.7622742951526504,0.7578420943311078,0.753395556834933,0.7490012580387515,0.7447302681053249,0.7406555942075159,0.7368494141124239,0.7333802406556219,0.7303098803769766,0.727689545417229,0.725553777369868,0.7239100137273641,0.7227212600712614,0.7218937205415055,0.7212966394039195,0.7207904121593216,0.72024675694322,0.7195627656163448,0.718670958505215,0.7175469244321454,0.7162156858208399,0.7147575529911728,0.7133138917597954,0.7120928932919566,0.71137507080591,0.7115177745829107,0.7129574667187539,0.7162077701775893,0.7218503266339458,0.7305141661807065,0.7428374833958152,0.7594032722155143,0.7806370319738738,0.8066507414832255,0.8370143550067056,0.8704523388896299,0.9045988169810679,0.9362313796077862,0.9621795437903055,0.9805042966087261,0.9912674444475857,0.9962429337632106,0.9979192718927747,0.9983975534973626,0.9984553901057921],[0.783163813937008,0.7796230196361609,0.7758611688771431,0.7719012185765144,0.7677746231566762,0.7635215874908454,0.7591908509530387,0.7548389244057198,0.7505287617998284,0.7463279286859508,0.742306405101758,0.7385341811767622,0.7350787063712341,0.7320019800336999,0.729356597986257,0.7271794187601127,0.7254807382700285,0.7242269794405968,0.7233292870295366,0.7226619324802698,0.722089671274218,0.7214878662527816,0.7207565540420527,0.7198305429759274,0.7186871022161909,0.7173523623523599,0.7159071746393529,0.7144928376770809,0.7133167653228165,0.7126578037482676,0.7128704691446096,0.7143868226290053,0.7177139656223556,0.7234241516961335,0.732133173827823,0.7444608812342928,0.7609652794240025,0.7820386170969471,0.8077506741049916,0.8376251895007905,0.8703638925053848,0.9036660863410014,0.9344865608576304,0.9598717676299189,0.9780238573887651,0.988968835389823,0.994317944455317,0.9963686449006398,0.9970610496390798,0.9971497771674138],[0.7839159103768798,0.78046929836954,0.7768072542246098,0.7729513603661075,0.7689311949123906,0.764784575383674,0.76055738724286,0.7563029359171816,0.7520808131011358,0.7479553329886147,0.7439936463586914,0.7402636370217268,0.7368315922053015,0.7337593688967021,0.7311003316944996,0.7288927314902306,0.727148532547083,0.7258367671962878,0.7248739277608726,0.7241402824975907,0.723505768130534,0.7228500223267719,0.7220765078452811,0.7211226843522858,0.7199677629707995,0.7186391461744683,0.717218284107274,0.7158463404359492,0.7147297248633162,0.7141451810299126,0.7144436780047874,0.7160517930811954,0.7194685340023455,0.7252545563383876,0.7340093964938972,0.7463305624365106,0.7627460315198454,0.7836090405399705,0.8089422328344157,0.8382234942789535,0.8701434184678652,0.9024840146183433,0.9323928844781026,0.9571455345446475,0.9750877636513128,0.9862108744914726,0.9919528495021085,0.9943982000007817,0.9953170163240728,0.9954445855649927],[0.7846763854075882,0.7813244997616682,0.7777628689859861,0.7740117686722617,0.7700990036433933,0.7660601487523825,0.761938423910599,0.7577841551248499,0.7536538175821381,0.7496087070800916,0.7457133184579299,0.7420334861481641,0.7386342170861262,0.7355768811235786,0.7329150030863465,0.730687352263666,0.7289066035312988,0.7275439222606728,0.7265212761092844,0.7257256316763621,0.7250328611087066,0.724327483410333,0.723516850947417,0.7225414182671299,0.7213825765072146,0.720069135566291,0.7186831689695237,0.7173655983619639,0.7163215567957214,0.7158251983084309,0.716223176172584,0.7179354463156485,0.7214513081164594,0.7273176024124812,0.7361146671042437,0.7484139348959409,0.7647089650403908,0.7853096474308616,0.8101892993571054,0.8387841433476004,0.8697869750604125,0.901077227161398,0.9300031502027686,0.9540703297844713,0.9717650693180111,0.9830457352151033,0.9891751848710107,0.9920165561036636,0.9931697535492692,0.9933502460119348],[0.7854432880195352,0.7821864573718875,0.7787256310570887,0.7750798503040603,0.7712752532986378,0.7673453178360211,0.7633307830095909,0.7592792115925715,0.7552441911655114,0.7512842089552667,0.7474612504581741,0.7438391318323618,0.7404814423724627,0.7374487147819163,0.7347940504431836,0.7325559683602529,0.7307471709412408,0.7293406919053469,0.7282639329971853,0.7274109695467171,0.7266642351377114,0.7259136902915782,0.7250710160735042,0.72407998449854,0.722924381442182,0.7216345319730519,0.7202931243127497,0.7190406921102654,0.7180807750503266,0.7176844025903729,0.7181930960157905,0.7200190138664361,0.7236401202574556,0.7295872719916038,0.7384188372961377,0.7506768530598162,0.7668169392924784,0.7871029473752136,0.8114592984929113,0.8392874336995351,0.869295748169173,0.8994723301954335,0.9273674435349147,0.9507100449512238,0.9681200269703294,0.9795249420145572,0.9860173067668507,0.9892413108895419,0.9906320467843519,0.9908818929316987],[0.7862147562504994,0.7830531061482561,0.7796932703452455,0.7761531311129334,0.7724572679028978,0.7686372051409045,0.7647313791448358,0.7607847928618755,0.7568483558652506,0.7529779318839265,0.7492331164423955,0.7456757137704504,0.7423677429943558,0.7393685555068975,0.7367302963703903,0.7344906104772896,0.7326617872740018,0.7312185838730267,0.730093703803803,0.7291884987431457,0.7283924226823452,0.7276013623538801,0.7267317291935966,0.7257309093348475,0.7245852732812,0.7233267412489589,0.7220385752713191,0.7208607382563426,0.7199948196321042,0.7197081488446524,0.7203362647527369,0.7222823368880563,0.7260113932674965,0.7320362466930151,0.7408907906513005,0.7530848927342728,0.769033727962487,0.7889540942852147,0.8127241574040136,0.8397190163491629,0.8686749926354621,0.8976964138600698,0.9245318586753193,0.9471219818460604,0.9642110753169028,0.9756983001228203,0.982515368762118,0.9860976245417402,0.9877239949700465,0.9880592519428909],[0.7869890171815688,0.7839224812561508,0.7806636262113273,0.7772292519758623,0.7736424862843708,0.7699330395532767,0.7661372142326659,0.762297641934694,0.7584627430883367,0.754685917912072,0.7510244653109548,0.7475381626732072,0.7442872986890158,0.7413297195518489,0.7387161549107301,0.7364829082667943,0.7346416015006918,0.7331686353071081,0.7320018353736137,0.7310498186444802,0.7302093444850369,0.729382610979875,0.7284911085484662,0.7274861004307147,0.7263567037252023,0.7251364855820149,0.7239092102528869,0.7228140538956925,0.722050264924176,0.7218808674876122,0.7226345506013994,0.7247043150029119,0.7285407201447414,0.7346366466686324,0.7434993596843221,0.7556044288039024,0.771325152385564,0.7908318127049667,0.8139606264299203,0.8400693831980738,0.8679329186833074,0.8957759399737341,0.9215379267443083,0.9433566958143443,0.9600906395418245,0.9716132489595132,0.978708039893048,0.9826164051034798,0.9844715811584391,0.984906148554632],[0.7877643864841568,0.7847927166374906,0.7816346449562337,0.7783059653097435,0.7748284580281202,0.7712301526058247,0.7675453755860294,0.7638145594903587,0.7600838032886503,0.7564041794720038,0.7528307603768378,0.749421265705318,0.7462340948673111,0.7433252991436452,0.7407438213596533,0.738524302677656,0.7366775746534461,0.7351816361774698,0.733979231583167,0.7329861087364368,0.7321064586143109,0.7312490632897692,0.7303407736965601,0.7293369508110835,0.7282295883093426,0.7270539231224507,0.7258941213271052,0.7248883276894784,0.7242330330709507,0.7241863341198174,0.7250692054925396,0.7272633407693136,0.7312034090463894,0.7373606990524743,0.7462141114939607,0.7582034868879576,0.773659864087677,0.7927088683379022,0.8151501732466663,0.8403331499200134,0.8670796862113317,0.8937359920541448,0.9184225008506475,0.9394583133724286,0.9558053657775678,0.9673144696037221,0.9746352246714627,0.9788324915582121,0.9809051897144592,0.9814497842839689],[0.788539267643465,0.7856620434356669,0.7826043774799445,0.7793811322089437,0.7760128406656008,0.772525976759172,0.7689530369414197,0.765332410070276,0.7617080206195985,0.7581287268435511,0.7546474251010298,0.7513197369571906,0.7482020243037997,0.7453482985848665,0.7428054358473062,0.7406062186588167,0.7387606544448824,0.7372483120299916,0.7360166395952876,0.7349882998652204,0.7340749083380265,0.7331919896049854,0.7322719599570168,0.7312744485119007,0.73019441932531,0.7290687722306295,0.7279819482246691,0.7270707928937786,0.7265286065636182,0.7266079336156986,0.7276211937228896,0.7299377057353309,0.7339749759716545,0.7401813156692304,0.7490059845001005,0.7608523674043424,0.7760098170716044,0.7945621938885183,0.816278619371962,0.8405082880691386,0.8661265736446812,0.8915998239081441,0.9152179209009538,0.935465084153201,0.9513965550803369,0.9628436529592429,0.9703369305019165,0.9747830226421602,0.9770581971854259,0.9777199031081737],[0.7893121509584601,0.7865287883845107,0.7835709771905172,0.7804527202314758,0.7771933980273302,0.7738180454610394,0.7703574619341902,0.766848131353997,0.7633319311466593,0.7598555992098771,0.7564698915496109,0.753228288005559,0.7501849831832239,0.7473917546813852,0.7448932189604307,0.7427202034421034,0.740881915104877,0.739359471671267,0.7381048059619774,0.737047227094847,0.7361056619622215,0.7352024290424396,0.7342756339547651,0.7332892884256006,0.732241380991052,0.7311704372942444,0.7301610225108148,0.7293483981833834,0.7289222346987483,0.7291289116949106,0.7302714977886074,0.732705967350152,0.7368315731289669,0.7430725693152649,0.7518477732948575,0.7635240594198198,0.7783504855173524,0.7963727734198651,0.817335642996071,0.8405953953398483,0.8650853331808909,0.8893886347478599,0.9119523349100072,0.9314100185851624,0.9469006628889607,0.9582393781541745,0.9658523422198445,0.9705060645543847,0.9729657099054496,0.9737479398415184],[0.7900816123946789,0.7873913722266282,0.7845326981969258,0.7815188018050608,0.7783679996226198,0.7751039946782909,0.7717560094669115,0.7683587456127995,0.7649521432068045,0.7615808972223315,0.7582936486426467,0.7551416947637029,0.7521769573708972,0.7494488388486188,0.7469995809887116,0.7448580354736687,0.7430326677807746,0.7415061249732826,0.740234604705321,0.7391537617769302,0.7381896403084234,0.7372713089330125,0.7363426065694386,0.7353719831961862,0.7343604639927903,0.7333481332240952,0.7324195087390625,0.7317079724961711,0.7313991292996824,0.7317326083333098,0.7330013947063527,0.7355472694101116,0.7397503464203685,0.7460100660749613,0.7547144695006297,0.7661944726213357,0.7806608855402156,0.7981253712821715,0.8183142330551172,0.8405970489230582,0.8639677165126741,0.8871215052395248,0.9086500938242832,0.927321525613482,0.9423497941167703,0.953537071965673,0.961219111926008,0.9660395098727573,0.9686634832105547,0.9695662128209949]],[[0.1345851521283475,0.13149639044373349,0.1278909225882057,0.12376126963686296,0.11913808933025175,0.11410749229660992,0.10883071482807798,0.10356242717468817,0.0986590958074995,0.09456215185207488,0.09173757306029799,0.09056695112465815,0.09122396696494908,0.09360685061912907,0.0973755722656147,0.10206690016793019,0.10721519943047123,0.11242982330912411,0.1174237440809059,0.12201020981136482,0.12608495812541587,0.1296050511326906,0.1325696425352177,0.13500456844296704,0.13695097772598358,0.13845751330210168,0.13957532540847659,0.14035518022215257,0.14084599624446895,0.14109423987149033,0.14114371870482645,0.14103542264056937,0.1408071830482188,0.14049305402342224,0.14012246373558113,0.139719321445729,0.13930136528072276,0.1388800593191698,0.13846126934695568,0.13804677005633167,0.13763640967613197,0.1372305577586798,0.13683236073344585,0.13644935995340793,0.13609416584659098,0.1357840718874304,0.1355396781872168,0.13538274853436147,0.13533364076035026,0.13540872196639403],[0.13397995776700128,0.1307109138741015,0.12687884159143883,0.12246792303852658,0.11750120734954193,0.1120600101408599,0.10630727941807629,0.1005117663107849,0.09506406891233943,0.09046598973865494,0.08726636272600027,0.08592854240881126,0.0866680106487009,0.08935978793089845,0.0935894913903811,0.0988069868294033,0.10447760114625344,0.11016885083554677,0.11557472979109354,0.12050430195568716,0.1248570740435288,0.12859730446005954,0.13173217166802914,0.13429505509927198,0.13633363380190375,0.13790197464228005,0.1390556810203373,0.1398492390310762,0.14033481714145282,0.14056190255230427,0.14057727928513308,0.14042497268314202,0.14014591278260974,0.13977721448553188,0.13935113551338985,0.1388939357993393,0.1384249861797976,0.13795651087469288,0.13749425958830264,0.13703919258886546,0.13658998206253578,0.1361458824761411,0.13570939570951707,0.13528819486458576,0.1348959430554616,0.13455187346982622,0.13427921418922345,0.13410271557941061,0.13404567026708747,0.13412690278891348],[0.13339061038909922,0.12994292717327052,0.1258846501051024,0.12119043239043754,0.11587388264004585,0.11000889644335617,0.10375679184970935,0.09739710455869918,0.09135351396840034,0.08619339709183856,0.08256340790463847,0.08102972296270664,0.08186260273886789,0.0849071233723909,0.0896544894733953,0.0954498244824119,0.10168123976556055,0.10787394040726293,0.11370585874270188,0.11898533436777047,0.12361847344477758,0.1275786856251964,0.13088236759975494,0.13357107562342374,0.1356992804690558,0.13732651055860326,0.138512744673607,0.13931607288420952,0.13979181400799706,0.13999243100571265,0.13996771932163105,0.13976486784102868,0.1394281248569755,0.13899795778284038,0.1385097791114681,0.1379925036944878,0.13746735812571537,0.13694741874288532,0.136438257763307,0.13593982234596053,0.13544932543932933,0.13496461321734915,0.13448731425360025,0.13402512466364583,0.13359279893482506,0.13321169533853008,0.13290797727397557,0.13270976649865732,0.1326436930967559,0.13273139320002494],[0.1328225911550461,0.1291998163186508,0.12491819808953236,0.11994174324528722,0.11427276645688406,0.10797486996405023,0.10120370332371616,0.09424489500408187,0.08755213719827534,0.08176218342724115,0.0776364560344728,0.0758714799194521,0.07681055809997181,0.08025954030169158,0.08558836485251563,0.0920159047673519,0.09884533622667105,0.105560975336303,0.11182916668006236,0.11746183264653424,0.12237483206654494,0.126552716281343,0.13002220094584946,0.13283351797531642,0.1350480559260544,0.13673072302811928,0.1379456975962953,0.13875448099220514,0.1392153858341646,0.13938376741701056,0.13931244752558652,0.13905190546506882,0.13864994545908346,0.1381507152415363,0.13759315677153716,0.13700919805346137,0.13642219085999902,0.13584618210712587,0.13528650372209278,0.13474186170782174,0.13420767763276026,0.13368004123501767,0.133159431618683,0.13265342850597042,0.13217790634501153,0.13175654433440423,0.13141877743037586,0.1311965267209982,0.13112021275375435,0.13121468539524855],[0.13228149756300472,0.12848921639774358,0.1239898205428932,0.11873569185040361,0.11271607294171725,0.1059812691555534,0.098676605300499,0.0910875764230101,0.08369212798054665,0.07719753078480118,0.07249835020381662,0.07045762009890877,0.0715179871108215,0.07543300735638507,0.08141488929958626,0.08853067824243739,0.0959924284949409,0.10324770126995277,0.10995753775614323,0.11594256016471846,0.12113174133242964,0.12552269450780712,0.12915338566149295,0.13208303635958565,0.13437991250628992,0.13611408263711924,0.13735364004338763,0.13816322176524573,0.13860391690048363,0.1387338486512226,0.13860885824887417,0.1382828405923097,0.13780741312767672,0.13723077218927301,0.13659582084855815,0.13593792227534313,0.1352828792862122,0.1346458618979889,0.13403190027062298,0.13343819897296477,0.13285799998443695,0.13228522484552704,0.13171887191662981,0.13116622899376817,0.1306443057935618,0.13017930753570847,0.12980430667202805,0.12955549779771466,0.12946760041581315,0.12956913420413257],[0.13177294130326805,0.12781887104862294,0.12311015013918226,0.11758676936788474,0.11122331493941623,0.10405383247082878,0.09620823117754604,0.08796411230821162,0.07981455109071345,0.07253401676093636,0.06716855924974587,0.06479527333248884,0.06599499817412488,0.07045015367728101,0.07716497196853038,0.08502502486501534,0.09314831328434982,0.10095343358238876,0.1081043683219576,0.1144362227688147,0.11989447843005721,0.12449152853016607,0.12827726586050492,0.13131997933397896,0.13369457580056338,0.1354759107133089,0.13673559059122953,0.13754102512871497,0.13795579910549602,0.13804063612272907,0.13785436644396146,0.13745442321623252,0.1368965151714177,0.13623330030438438,0.1355121394832909,0.13477232802883407,0.13404251412214122,0.13333918691305577,0.13266701847160003,0.13202141653434116,0.13139299116420236,0.13077301041414183,0.13015859684860068,0.12955652863989747,0.12898494914648798,0.12847280212797538,0.128057193349494,0.12777911413340087,0.12767815229191964,0.12778701393575934],[0.13130243433789268,0.12719647042455545,0.12228989125822937,0.1165098181131391,0.10981492445261345,0.10222029674297357,0.0938352134199933,0.0849203175763427,0.07597082523418465,0.06781826081309089,0.06167538848309113,0.05889549646594292,0.06025661889682037,0.065342120860957,0.07287799174192255,0.08153558706639336,0.09034177644906902,0.09869859676181057,0.10628312428366118,0.11295111398067263,0.11866774650372888,0.12346155762831593,0.12739469908734385,0.13054431910522513,0.13299150721354897,0.13481536588486595,0.1360904903401269,0.1368866101530845,0.13726946016952396,0.1373021523317605,0.13704645024336576,0.13656344410281115,0.13591323326672364,0.13515339922318167,0.13433633092264344,0.1335058404832961,0.13269389850574995,0.13191856456469403,0.1311841067430387,0.1304838026094991,0.12980510474910656,0.12913605759427735,0.1284714393863843,0.1278172522340154,0.12719275046084436,0.12662983374044365,0.12617006614114754,0.12585981024792098,0.12574415792378457,0.1258605861990498],[0.13087526608472483,0.1266294714064219,0.12153955942463085,0.11551966182694837,0.10851175093969129,0.10050978135966962,0.09159750692651289,0.08200880044866528,0.07222412136321212,0.0631123540450676,0.05605932121162621,0.05277404013977669,0.05432408858795688,0.06015112106241068,0.06860325715477884,0.07810484332993904,0.0876040389813227,0.09650407145034322,0.10450679115574206,0.11149470747468757,0.11745539270606901,0.12243436679825927,0.12650594103980112,0.12975558561456085,0.1322698724591565,0.13413143676281863,0.1354172131625576,0.13619870879086413,0.13654339835224064,0.13651652471934125,0.13618270196764037,0.13560679021748476,0.1348535995814314,0.1339861489661624,0.1330625081084361,0.13213169246797624,0.13122957176482297,0.13037609713789675,0.12957510436228267,0.12881736695165452,0.12808657087943454,0.12736686903847075,0.12665014255565202,0.12594129527413256,0.12526064423379324,0.12464326377392004,0.1241356284985476,0.12379009954256827,0.12365798051314074,0.12378217980401117],[0.1304963754965416,0.12612490552298244,0.12086919343307853,0.11463067788924726,0.10733444032564696,0.09895193788271932,0.08953738945037651,0.07928828816295856,0.06865034496063252,0.0584981612541852,0.05037829713564648,0.0464524135316571,0.04822683413903717,0.05493404398685194,0.06440146614968734,0.07478074822920633,0.0849678436743479,0.09439033629936297,0.1027872258339256,0.11007320973836603,0.11626011525914867,0.1214106035469292,0.1256105376852675,0.12895280949284035,0.1315285187216626,0.13342294252057021,0.13471458312809603,0.13547609645964764,0.13577622424681562,0.13568203742225896,0.13526088833494002,0.13458151085671025,0.13371376488751074,0.13272667495047177,0.1316847354248904,0.13064296933093103,0.1296418418001392,0.12870360460896693,0.1278316600840306,0.12701386102143805,0.1262294223189126,0.12545782477198572,0.12468740339563149,0.12392157851381816,0.12318165124789111,0.12250608615965537,0.12194674428012353,0.12156266553844047,0.12141215037415355,0.12154428387395737],[0.13017022264085434,0.12568918171069546,0.1202880508529073,0.11385632624782555,0.10630271072685538,0.09757586653961821,0.0876979710035159,0.07682206373789661,0.06533811153164551,0.054082292690917154,0.04471637266012477,0.03995956745370546,0.04200581119080171,0.04976758901054139,0.06034587083587402,0.07161571186252212,0.08246612061659939,0.09237641136745868,0.10113443168439,0.10869109247297144,0.11508317396311163,0.12038980678688024,0.12470723146630065,0.12813447830332647,0.1307659633340047,0.13268854315298187,0.13398140017815072,0.13471763011339208,0.13496671009848202,0.13479719140022026,0.1342790205726017,0.13348489557939913,0.132490080234744,0.1313702275818093,0.13019709981032204,0.12903266661061588,0.12792282782876402,0.12689265528547933,0.12594515670567896,0.1250648031658621,0.1242255252708414,0.1234012213931813,0.1225759220784931,0.12175110853285713,0.1209489520397141,0.12021151386705234,0.11959653523302921,0.11917046652265163,0.11899947260404696,0.11913965530138844],[0.12990066501380884,0.12532789246543538,0.11980430080053475,0.11320865698570576,0.1054345565727382,0.09640883312536011,0.08612119637042297,0.07467525657208905,0.062386815103639734,0.050000751272796976,0.03919824931002071,0.033335038393043914,0.03571981925983298,0.04475545667703492,0.05652256575945393,0.06866466001777465,0.08013020613464414,0.09047863765857345,0.09955579273636647,0.10735063069318826,0.11392412135541195,0.11937025896422826,0.12379388875927175,0.12729851064436104,0.12998039682962262,0.13192676112547252,0.13321647500708597,0.13392229429906016,0.13411384693492395,0.1338607732511928,0.13323543501222523,0.13231456499738856,0.13117919384980767,0.12991227866216826,0.12859379880632907,0.12729376304892473,0.1260645156035639,0.12493460579040447,0.12390674256849563,0.12296150943564925,0.12206661533923191,0.12118931624180673,0.12030845606684529,0.11942304406403179,0.1185559678228927,0.11775307531198756,0.1170784908680905,0.11660685446879246,0.11641315002642194,0.11656144165355915],[0.12969084417396357,0.1250456329073855,0.11942473038976913,0.11269782488185547,0.10474542904141612,0.09547485974050314,0.08484541328183133,0.07291085654690928,0.059901673208992354,0.04642056321217863,0.03401327597634814,0.02663608929229289,0.029458933939703818,0.04003775598437139,0.05302890192219014,0.06598194737626303,0.0779876559366914,0.08870936145914625,0.09805531664191484,0.1060514776559511,0.11278057353159927,0.11834887311439089,0.12286745585423674,0.1264422526187839,0.12916970309267603,0.13113601596223584,0.13241867392604192,0.13308925549847703,0.13321690958469876,0.13287193281996154,0.13212888457266478,0.13106857539590955,0.12977816498901623,0.12834863710562486,0.12686924854569562,0.12541931198284212,0.12405882768863019,0.12282065224462037,0.12170737117717395,0.1206951307790734,0.11974433907917383,0.1188143766631057,0.11787787907214126,0.11693076759869353,0.11599644845089252,0.1151247205979555,0.1143865911055072,0.11386570897949126,0.1136469223790271,0.1138033205676776],[0.1295430882838845,0.12484584261135916,0.1191544826445844,0.11233164382421691,0.10424745449667978,0.09479330380935479,0.08390269605889505,0.07158460386557029,0.05798483999935243,0.04353300972217592,0.029450801317157736,0.01995800683678242,0.023376772938219176,0.03580092283861702,0.04996859771064843,0.0636170450521124,0.07605978784577004,0.08707562709492779,0.09663294696078872,0.10479031062759263,0.11164804009707305,0.11732112635397143,0.12192395041224349,0.12556250087099355,0.12833149905349653,0.13031467306664102,0.13158697423846322,0.13221792480260586,0.13227552939315426,0.13183026943043155,0.13095864128607276,0.12974553799625946,0.12828459649012483,0.12667558671389528,0.12501821517563347,0.12340255477587928,0.12189771195660211,0.12054189492431844,0.1193378503642969,0.11825669748528184,0.11725030166023964,0.1162687345001437,0.11527724445584606,0.1142679615485286,0.11326456670373095,0.11232093723966262,0.11151544183563179,0.11094158681457127,0.11069522257561741,0.11085965655634976],[0.12945883575177458,0.12473067960984119,0.11899684348657608,0.1121152153302825,0.1039487603775904,0.09437757153627571,0.08331623435009801,0.07073932828838272,0.05672274614680325,0.041531121453887036,0.025931827382274654,0.013510233332046864,0.01777697026127422,0.03228092170114151,0.04744206989958832,0.06160923331411298,0.07435919767157098,0.08557800925429432,0.09528401030543056,0.10356058117266416,0.11051983156559415,0.11628105031516614,0.12095849461261984,0.12465555584244904,0.12746319595014888,0.12946110771479788,0.1307205303407211,0.13130802865553537,0.13128977411871712,0.13073592622491334,0.1297246096839595,0.12834475341965762,0.12669678771361606,0.12489004901112526,0.12303597378194919,0.12123706071924306,0.11957325222206219,0.1180894192139032,0.11678890273517409,0.1156371719188637,0.11457612127847332,0.11354484598060474,0.11249985259815094,0.11142868796268961,0.11035501782219923,0.10933687466256777,0.10846042322228364,0.10782988729662912,0.10755335064925971,0.10772567595450312],[0.12943858436209818,0.12470093469773517,0.11895309345912053,0.11205066286461399,0.1038529766062218,0.09423412259557072,0.08309817540140661,0.07039974069831324,0.056171848770814964,0.04056819849397587,0.023966314953978714,0.008020973153915178,0.013345483727259282,0.02974198658980537,0.045531577834193294,0.059981974226602675,0.07288758199119551,0.08420972643989702,0.09399886052675537,0.10235239961304467,0.10938705970068963,0.11522128724003282,0.11996539505547549,0.12371730811786075,0.12656208360970592,0.1285737847175299,0.1298187503779494,0.13035968703772668,0.13026023410262627,0.12958969166405943,0.12842745041383838,0.12686636153314848,0.1250139094012759,0.12298977434797242,0.12091849952515862,0.11891689878300926,0.11707780588914123,0.115454396384983,0.11405123952336116,0.11282751079732929,0.11171349110541405,0.11063535724258527,0.10953932165999256,0.10840747049522508,0.10726312279204274,0.10616847633278849,0.10521785015513233,0.10452703349855595,0.10421766565592386,0.10439766045672241],[0.12948186910837653,0.12475599210212983,0.11902243614115071,0.11213699688343191,0.10395896843237816,0.0943619037208547,0.08324830059734241,0.07056888222816605,0.056347057600017625,0.04070923472091825,0.02392467539863741,0.006552024049538051,0.011458948179393724,0.028408172350131947,0.0442835193541202,0.0587380655968252,0.07163423266100623,0.08295616270606962,0.09276276943953486,0.10115257568407479,0.10823874201408652,0.1141332180100943,0.118938273005027,0.12274335976051709,0.125625438508174,0.12765135371214334,0.1288813828367847,0.12937349803339354,0.12918811335007918,0.12839310672019236,0.12706871288061505,0.12531150631735608,0.12323620166056722,0.12097356461825823,0.1186626964177006,0.11643684777535668,0.11440417474657975,0.11262820867203525,0.11111565049811035,0.10981873852214517,0.10865424976672682,0.10753317588690664,0.10638966110448558,0.10519937700101656,0.10398493340364647,0.1028126178419465,0.10178514370716096,0.10103066857770548,0.1006857953471703,0.10087315929035573],[0.1295872704728327,0.1248938398827066,0.11920201003987833,0.11237012515478798,0.10426083454637389,0.09475229905467099,0.08375380095557863,0.07122720169296243,0.05721741589081842,0.041903465882703377,0.025741458042729096,0.010676252503246919,0.013070283296184917,0.028358333072878255,0.04369369740467163,0.0578568276965388,0.07057550704479706,0.08179488371354941,0.09155609266294693,0.09994482704283164,0.10706201635021148,0.1130071655208545,0.11787024685391785,0.12172918141223228,0.12465065556457906,0.12669275943102476,0.12790861194706074,0.12835062724786878,0.1280753236402848,0.1271485756767832,0.12565097497704106,0.12368251464529363,0.12136519574065423,0.11884153092487822,0.11626666994571765,0.11379265292962948,0.11154581669592123,0.10960260438044467,0.10797311323699318,0.10660203339151407,0.10539046160868032,0.10423154917710557,0.10304534735406291,0.10180010083265406,0.1005173365936373,0.09926724864799061,0.09816101174393321,0.09733986588059378,0.09695686276397558,0.09715121950694522],[0.12975245325373527,0.12511113034863958,0.11948698469638805,0.1127430102464844,0.10474817569850126,0.09538961377813455,0.08459021428529526,0.07233456468548162,0.05871105456757662,0.04399898175985094,0.028951441417015313,0.016422021100298983,0.016986547255007273,0.029464309801184006,0.04370250233900457,0.05729423374826436,0.06967542347856862,0.08069617157186099,0.09035471322774848,0.09871015562009264,0.10584246585200593,0.11183267381328263,0.11675416688369203,0.12067030471273092,0.12363540273254968,0.1256973656076455,0.12690116019883957,0.12729290001213336,0.12692457920000919,0.1258594777231939,0.12417798706088322,0.12198308684600123,0.1194039594105537,0.11659538929011909,0.11373005052973632,0.11098133875166447,0.10849710839937414,0.10636989049663226,0.10461492597907404,0.10316882891077644,0.10191450834777173,0.1007241498656163,0.09950140108260529,0.09820603865301929,0.09685815504166324,0.0955315344622292,0.09434563592916131,0.09345535043803148,0.09303172800102945,0.09323263310398155],[0.12997423436319416,0.12540328762607555,0.11987073552066081,0.11324596301012549,0.10540660925908561,0.09625203167624923,0.08572336254865882,0.07383468068010712,0.06072739692500558,0.046788861714955866,0.03300861089172481,0.02234702590872058,0.021761830318735773,0.03144165543703379,0.04420314996059717,0.056986108175131986,0.06888732327082724,0.07962403451451959,0.0891307393942439,0.09742738065397831,0.10456454936096962,0.11059886055484812,0.11558290061713525,0.1195625483223467,0.12257779648927518,0.12466509042987765,0.12586039566582724,0.1262028937407795,0.12573948883727307,0.12453027570737524,0.12265481623261597,0.1202184955837512,0.11735736446460643,0.11423879688638003,0.1110543755454851,0.10800159019802866,0.10525367179996173,0.10292317269447784,0.1010328695160607,0.09951093288976495,0.09821919411487617,0.09700517114722353,0.09575346593637714,0.09441436242503934,0.09300624049797829,0.09160599649661517,0.09034086124026315,0.08937972812255837,0.08891324216543185,0.08912019864659874],[0.13024867645229515,0.1257646566092169,0.12034508625550142,0.11386704938256431,0.10621847978566719,0.09731292564473785,0.08711195668750929,0.07566085788665451,0.06315198738467805,0.050059095632731844,0.037487268317348534,0.02811584090655121,0.026705418581615632,0.033962952971593505,0.04505948228247509,0.05685363745037798,0.06815634628257103,0.07853758860842967,0.08785341158010261,0.09607380836285109,0.10321212814614168,0.10929483809502942,0.11434966540512129,0.11840227454408668,0.12147659529811568,0.12359655064205909,0.12478844116905612,0.12508402720781228,0.12452464175285477,0.12316661748999883,0.12108798565423814,0.11839578784653546,0.11523237301555872,0.11177773005574586,0.10824353813806734,0.10485421699115169,0.10181278150999286,0.09925665609511107,0.09721940533994602,0.09562066759949574,0.09429786640376607,0.09306943298015712,0.09179788902304768,0.09042308327254339,0.0889615559375319,0.08749264299442189,0.08615038271428985,0.08511771694772013,0.08460650890707158,0.08481899365885755],[0.13057120289946886,0.12618868516263956,0.12090060360336136,0.11459257948235797,0.10716369909695848,0.09854236611627744,0.08871046641550054,0.07774188217310245,0.06586960727343852,0.053618857078490074,0.042102906581057156,0.033604767367268716,0.03152032032461648,0.03674043821199432,0.04612589457299765,0.05680990283980627,0.06742234940286994,0.07739267277780743,0.08649016023643695,0.09462601296183755,0.10176907730385226,0.10791019659195462,0.11304840341822064,0.11718667224662617,0.12033140703931287,0.12249321053580159,0.1236882816259876,0.12394064288852592,0.12328568255021387,0.12177542435536157,0.11948560213098927,0.11652398264486184,0.11303833660735152,0.10922090328543184,0.10530431108914298,0.10154271915143284,0.0981738756342777,0.0953660251953099,0.09316791984693516,0.09149103499361923,0.0901445560108009,0.08891250303615314,0.08763180441018253,0.08623110523831132,0.08472524250219263,0.08319508775773277,0.08177992246746069,0.0806763726279413,0.08011914670313762,0.08033665218247468],[0.1309367287239777,0.12666812981810283,0.12152692586302395,0.1154076437112517,0.1082206435453823,0.09990866978180711,0.0904718866808735,0.08000710348974799,0.06877345314511145,0.05731211264584607,0.046673337055403635,0.03875069003579882,0.03606267970394488,0.03955301098004115,0.04726322317137192,0.056766152339175785,0.0666228831129099,0.07614355115190914,0.0850077537172402,0.09306070280514596,0.10021996948631748,0.1064355416802404,0.11167419291141775,0.11591406046898908,0.1191429052547952,0.12135753115941944,0.1225638652243427,0.1227780779094115,0.12202937028486478,0.12036495992131861,0.11785746348440815,0.11461425433184931,0.11078729857629324,0.1065802248786105,0.10224695306806417,0.09807397558988448,0.09433920033433839,0.09124892894177163,0.08887302831912904,0.08711591195718758,0.08575413969394738,0.08453083692830694,0.08325322227377083,0.08183826775120646,0.08029966749903725,0.0787186499297445,0.07723738808383848,0.07606529744604681,0.07546154217652982,0.07568363939911579],[0.13133980141977528,0.12719527442653833,0.12221310656066042,0.11629666047507914,0.10936704048137548,0.10137985431328371,0.09235013554695694,0.08239026579183091,0.07177022779153082,0.06101784163899743,0.051082151998224634,0.043516471606170094,0.040254320599052894,0.04224157316460636,0.0483483503405909,0.05663694733510539,0.06569591490662192,0.0747445753207053,0.08337348224822311,0.09135564885147378,0.09855081977535121,0.10486307873798192,0.11022368841204067,0.11458420568814515,0.1179130478207769,0.12019311412362098,0.1214201933583712,0.12160271858607323,0.12076361578359288,0.11894487202383884,0.11621513545131203,0.11268008827232945,0.10849428529131902,0.10387127971614522,0.09908590192093085,0.09445908158684864,0.0903146292468591,0.0869056085054387,0.08433095859302839,0.08249028187009297,0.08112252995861893,0.07992194423945058,0.07866112842313153,0.07724537705384774,0.07568845075582836,0.07407042938903394,0.07253300133984292,0.07129681754297233,0.07064708091576206,0.07087351186059505],[0.13177474556042723,0.12776215127733392,0.12294795489644669,0.11724390359631687,0.11058078770118118,0.10292490315049588,0.0943019425703448,0.08483201594785349,0.07478209231227094,0.06464555257074694,0.055254994219990174,0.04788025113101487,0.04405060526692676,0.0446956202187892,0.04927837524038996,0.05634385353175776,0.064582107186708,0.07315171476992284,0.08155633898449077,0.08949065984857776,0.09674988321291468,0.10318723576564473,0.10869558117801434,0.11319864416971791,0.11664529032482296,0.11900483340043873,0.12026339359998543,0.12042203305905409,0.11949749099337306,0.1175261992381246,0.1145719860851395,0.11073739200148704,0.10617756573277033,0.10111382148003319,0.0958405539246453,0.0907143644231236,0.0861107139366931,0.08233972346087166,0.07954004447675866,0.0776105107512191,0.0762468970576872,0.07508458942724512,0.07385560196641923,0.07245422918451475,0.07089646881042976,0.06925935328182792,0.06767938417521724,0.06638610882928939,0.06569233729463442,0.06592314735742387],[0.13223580527532955,0.12836075498106936,0.12372035702992899,0.11823398342731249,0.11184066547948351,0.1045147863051625,0.09628819495719797,0.08728127219086157,0.07774663932728308,0.06812982891863481,0.059145475752410075,0.051831335954203625,0.04742738902624426,0.046840946651071094,0.04997132327098004,0.05581776351531218,0.06322657732790997,0.07132390614903593,0.07952817920357394,0.08744859875206629,0.09480850018704154,0.10140531679954543,0.10709106963798865,0.11176099899532498,0.11534478496726816,0.1177989475312233,0.1191007693955526,0.11924457622295886,0.11824120388277255,0.11612133318581765,0.11294316413389452,0.10880454125325133,0.1038588512794282,0.09833224510044285,0.09253611709519935,0.08686260755478678,0.08174404229847917,0.07755946120380876,0.07450137632684074,0.0724746794691882,0.07112592893789481,0.07001904027371511,0.06883796327733842,0.06746763064555959,0.06592984032903847,0.06429619234949495,0.06269158742799837,0.06135124580616163,0.06061719836496093,0.06085292232974368],[0.1327172792793078,0.12898324076189774,0.12451956534477937,0.11925226286667441,0.11312691729585267,0.10612321996174955,0.09827478283171956,0.0896957272674218,0.08061581875237331,0.07142541996266433,0.06272689091643024,0.05536834431165892,0.050375206254155376,0.04863073698756324,0.05036518304473118,0.05500016096011202,0.061580160251543045,0.0692242127190423,0.07726486168569711,0.08521644701927751,0.09272198878601774,0.09951817706633909,0.10541432724035067,0.11027727916014357,0.11401855423600335,0.11658318372945915,0.11794081974869948,0.11807996106681455,0.11700603253066473,0.1147439277590919,0.11134550694596253,0.10690233674786621,0.1015633988124652,0.09555599410408608,0.08920450759050073,0.0829345087505466,0.07723900936295154,0.07257906220820216,0.06921968712663575,0.06708298920915026,0.0657601354798066,0.06472738193244298,0.06361097088196867,0.06228942794637353,0.0607959026934959,0.05919355239157774,0.05758704840005987,0.05621314093499279,0.055444888666140814,0.05568680633953602],[0.13321364396825627,0.12962210052358603,0.12533544639511116,0.12028519682434685,0.11442169011081538,0.10772717496873072,0.10023302365760853,0.09204175701672637,0.08335442272886406,0.07450326636931581,0.06598721650836267,0.058498243424705575,0.05289650407107187,0.05003972865554226,0.05041647131761655,0.053843698602018084,0.059600249542688256,0.06682081999195322,0.07474740129995742,0.08278643675448157,0.090490586361995,0.09753090897878462,0.1036729518427953,0.10875614547938545,0.11267562696560973,0.1153667845711597,0.11679322196197765,0.11693879080203756,0.11580421263182902,0.11340874709825943,0.10979736354591299,0.10505384513611694,0.09931997109247725,0.09281983648456828,0.08588522669177004,0.07897037899898492,0.07263013858638949,0.06742097347891127,0.0637046101013347,0.0614382683141647,0.06015220411560604,0.059213923551878926,0.05817909581795869,0.05692456410436904,0.05550320026119797,0.05396585942328129,0.05238546852909101,0.050995335698515665,0.050201852383729595,0.05045233155974939],[0.13371966108032415,0.13027031194064193,0.12615868182372683,0.1213205903445246,0.11570933666192766,0.10930716130152605,0.10213975725272963,0.09429395461019645,0.08593846930710848,0.07734740367679316,0.06892596251888616,0.061235778352107514,0.0550042898068615,0.051060649361770884,0.05009901062890303,0.05231243739667497,0.057251315999428246,0.06408792233563622,0.07196318952786313,0.08015728452051073,0.08812044349581871,0.09545352361306914,0.10187837610552578,0.10720912492113262,0.11132712280062443,0.1141605074406759,0.11566877068319134,0.11583254686004067,0.11464877386643238,0.11213144583971495,0.10831832015621895,0.10328409707222605,0.09716060044759918,0.09016391734657088,0.08262610666708184,0.07502204266523724,0.06796512428453189,0.06211897707881787,0.05797255686950652,0.055546631171205355,0.0543074153505976,0.053485741234419536,0.05254891867519286,0.0513791892284084,0.05006152186709717,0.04862938288090243,0.04710861813744378,0.04572360041090786,0.044917436342828077,0.04518037924806803],[0.13423046747541756,0.13092145770910515,0.12698091983982293,0.12234777608389266,0.11697659033294065,0.11084732372189138,0.10397719734686212,0.09643444971278144,0.08835364776039983,0.07995255835128123,0.07155206742019142,0.06360306638724428,0.0567214785744232,0.051702245972932534,0.04940328542817715,0.05038204816763594,0.05450520263505648,0.06100658256051917,0.06890737302991853,0.07733557402284869,0.08562467029723585,0.09330160432729445,0.10004621202844914,0.10565075151722199,0.1099862697483007,0.112976566826328,0.1145792671752134,0.11477342910739541,0.11355332254591267,0.11092827803562666,0.1069288191820775,0.10161961841365007,0.09512009791195693,0.08763347000728955,0.07948374286688302,0.07115480125884467,0.06330877239074377,0.05672286610054605,0.05204969824660995,0.04941839002633335,0.04823413065322744,0.04755343709152214,0.046729726253993756,0.04566086389109186,0.04448205402596942,0.043202393094137835,0.04178011438473501,0.04042530343840175,0.039623301676054795,0.03990470323634588],[0.1347416456268623,0.13156981383559088,0.12779487764748068,0.1233577159641289,0.1182126279801708,0.1123353855981437,0.105732612108133,0.09845211814264257,0.09059388608945061,0.08232224537644074,0.0738823765465282,0.06562923097471693,0.05808058011260264,0.05198841472500006,0.04833659189251181,0.048040255353799334,0.051341282940098536,0.05756568137665381,0.06558452476892249,0.07433734575754837,0.08302442443287379,0.09109689637491869,0.09819649474004423,0.10409860852987174,0.10866833876070965,0.11182851017354047,0.11353735405125148,0.11377414654812067,0.11253177074059705,0.10981573538472453,0.10564966900586338,0.10008777856214147,0.09323525414595497,0.08527804679631479,0.07652333819167405,0.06744913770424461,0.0587479277687363,0.05130560233326128,0.04597703858641966,0.04306944252240752,0.04194437699825596,0.04143228157756792,0.04073445520063306,0.0397789092675059,0.0387777707858939,0.03770566095863272,0.0364253121199115,0.03512853409823747,0.0343524741055315,0.03466108120140491],[0.13524927438582435,0.13221040735735243,0.12859439743189685,0.12434303460947085,0.11940903832028812,0.11376247564159113,0.1073978904966714,0.10034174705160136,0.09266004846813349,0.08446720793133065,0.07594042801374458,0.06734998371101106,0.0591234974368331,0.051958075532969036,0.046924153921679264,0.04528784181666345,0.04774655270136142,0.05376313298866883,0.0620108056825193,0.07118995513285334,0.08035000783372409,0.08886777753087058,0.09635378130230367,0.10257324371257183,0.10739047959700405,0.11073101957511024,0.11255629282838757,0.1128476594105902,0.11159801570629338,0.10881012099150433,0.10450145106653037,0.0987159542733779,0.09154369571831249,0.08315012962588712,0.07381759104495425,0.06400152744063875,0.05439712630364884,0.04597439124976741,0.03981974993124118,0.0365236865587934,0.03545458926167342,0.03514414555780047,0.03458131324617914,0.03374498191480448,0.032964303333696834,0.03216377494117291,0.031071676987886584,0.02986103765013885,0.029137924822489638,0.02948594812141833],[0.13574996042782578,0.1328390451216368,0.12937446012829334,0.125297993820367,0.12055971383759682,0.1151228681437865,0.10896903702886822,0.10210319301848103,0.09455874699368164,0.08640407671131918,0.07775537300832727,0.06880707318535025,0.0599012486737506,0.05166547923408466,0.04521138401392897,0.04214068345718122,0.043715710375450384,0.04960766028875094,0.058216907310459094,0.06793424521366477,0.07764189821807942,0.08664952935542544,0.09454705082684185,0.1010979283289351,0.10617144417087364,0.10969963438121302,0.11164968464054482,0.11200687682159305,0.11076557771798783,0.10792707152545515,0.10350384233682393,0.09753052831283661,0.09008239515523447,0.08130301723543844,0.07144420369503071,0.06092328740717769,0.05040376903803557,0.04088746295354369,0.03368578369190548,0.029818027690381367,0.02878669652516272,0.02872137601122593,0.028296969381807,0.027574005959043003,0.027061871160029626,0.026608482498586758,0.025750622284170042,0.024649231380957613,0.02401056316282723,0.024414329063239763],[0.1362408514954958,0.13345231619539571,0.13013116226742957,0.1262184180632817,0.12166068334063097,0.11641366254523011,0.11044562598238904,0.10374055327172943,0.0963012450203066,0.08815415942584989,0.07936091708875463,0.0700475224546028,0.060473419205580047,0.05118059070785837,0.04326745091007343,0.038633640888072425,0.03925127127250831,0.04512167026683458,0.05425219335755099,0.06462702242660762,0.07495157459883828,0.08448429806920303,0.09280934496661428,0.09969823251814033,0.1050311878245727,0.10875039405534058,0.11083113831317519,0.1112643181077051,0.1100472090799714,0.10718104779954536,0.10267488444577515,0.09655576890336412,0.08888588710270848,0.07978798022666934,0.06948165669085701,0.05833597090071339,0.04694962711312986,0.03627706979655069,0.027765771785142127,0.023015270786448824,0.021970232706097343,0.022216532856847392,0.021924266880415797,0.02128579106871611,0.02110003714093065,0.02108762249760675,0.020503660925505405,0.01951820970669738,0.01899654164634124,0.019476875551694996],[0.13671963310195992,0.1340475711379805,0.13086166179233927,0.12710158102029886,0.1227099008308356,0.11763442365263196,0.11183023751976066,0.10526136071256226,0.09790243087295435,0.08974229880004768,0.0807942087017308,0.07112258300603627,0.06090713301071102,0.05058905220906614,0.041190142030358895,0.034827916072952755,0.034363763282591796,0.040346315773593,0.05019060207665065,0.06134367864854949,0.07234189675777938,0.0824206030939423,0.09117708672268952,0.09840139634460625,0.10399034604214824,0.10789940634413263,0.11011389458614619,0.11063174984734338,0.10945449162385,0.10658482051364686,0.10203024349214142,0.0958126644481605,0.08798431123331941,0.07865083448027835,0.06800318930038847,0.05636182016412985,0.04424245834574131,0.03247134990181863,0.022420982281511875,0.01624765008934019,0.015048733508794149,0.015734854212683842,0.015547110720669109,0.014908664656044538,0.015132403680188177,0.015692445154701726,0.0154026205151927,0.014495990709457555,0.014113907882838695,0.014695913208816674],[0.1371845107563937,0.13462288177756618,0.13156409896525592,0.1279460628563416,0.12370700462267757,0.11878679994766807,0.11312789234293114,0.10667580905454051,0.09937984657369422,0.09119576123444441,0.08209463275884764,0.07208635017207396,0.061275326759651375,0.04999101993599796,0.03911139963336396,0.030825123129687777,0.029072086145303374,0.035351086716756484,0.04613891845396161,0.058180499035577385,0.069886670999063,0.08051223119010464,0.0896890258021719,0.09723548911076582,0.10306959427046108,0.10716235287091326,0.10951042024221405,0.1101198146915264,0.10899744378910861,0.10614898305018762,0.10158251454352449,0.09531781258557495,0.08740147155854724,0.07792828714998974,0.06706949746030556,0.05510891145940117,0.042489755382793336,0.02988416264699902,0.018348887572826426,0.009928515557026795,0.008116236403289056,0.009592380999074697,0.009411149070065034,0.008494520158535001,0.009303656285266599,0.010661363735655434,0.01062572603939687,0.009637150074995531,0.00936932463213442,0.010081048475760303],[0.13763418002713362,0.1351769853228117,0.13223749842042784,0.12875158719706067,0.12465305891123041,0.11987413430663045,0.11434549775347634,0.10799601332829095,0.10075276397545102,0.09254313946732724,0.08330249738167801,0.07299401959540083,0.061654149701113034,0.049497966424288956,0.03720138518829431,0.026794485433592755,0.023404260015659477,0.030253265568975566,0.04224757795781821,0.0552556484159418,0.0676689076984478,0.07881636360563062,0.0883847863436012,0.096228370220505,0.1022889114328553,0.10655395205979837,0.10903199072015035,0.10973767112733182,0.10868416069931608,0.10588152555043391,0.10134062919273444,0.0950824759320454,0.08715315004752824,0.07764459512066517,0.06672138914975678,0.05465329064146447,0.04185247656184117,0.02891289071568305,0.01664803119365208,0.0061501131006843355,0.0021854416579082203,0.005482239415366806,0.004927956345567241,0.002367672665650985,0.004432411078830727,0.006864875229100251,0.006807006616588824,0.00518163208769162,0.004761224622460146,0.005629513098670117],[0.13806778688350585,0.13570921665305682,0.13288165814492853,0.12951884598904775,0.12555028834137566,0.1209010790157092,0.11549131576948257,0.10923531178885575,0.10204130892179945,0.09381327175167152,0.08445763328972987,0.07389981954395206,0.062119429640202645,0.04922655067203346,0.035666083729443646,0.023023550026724175,0.017399439455986092,0.02525956459761184,0.038722143412203126,0.05270703664619662,0.06577722650112726,0.0773908474846872,0.08730304186616213,0.09540649245830529,0.10166678224595482,0.10608740692112213,0.10868828376397945,0.10949266518430406,0.1085205108644586,0.10578750306473034,0.10130942117085626,0.09511191242844122,0.08724591685901836,0.0778091526670307,0.06697416297172167,0.0550235952834141,0.04239437155289964,0.029738277070202945,0.018043283592643518,0.009122575818946078,0.006669016105659172,0.007918358859637665,0.007057148586881157,0.004850169876045889,0.005341112521753999,0.006790967767584652,0.006028804898701357,0.0031718129966901995,0.0007092202027650617,0.0014593623407890635],[0.13848488077306878,0.13621943249992366,0.13349703074805355,0.13024931951569976,0.12640181463242756,0.12187322507060148,0.11657446266629548,0.11040761682812839,0.10326564166673428,0.09503419689107699,0.08559795686382458,0.07485472602203228,0.062742357071952,0.04928918025877109,0.03473036267502692,0.0199942736962945,0.011116207455481978,0.02075483076218926,0.03582796480066386,0.05068454139494632,0.06430002450530033,0.07629066230836698,0.08647941170928876,0.0947936199524391,0.1012193874992104,0.10577387143154993,0.10848700901563009,0.10939005506294489,0.10850991085243591,0.10586882493886947,0.10148939309882204,0.09540506318679966,0.0876766264565305,0.07841551871167743,0.0678153544665,0.05619462324258558,0.044058151781865784,0.03220046770466773,0.021915798213037158,0.015267288695398451,0.013542694573423546,0.013733249001869634,0.012797968268369368,0.011157153347452015,0.010576848103299421,0.010463338339312605,0.009046137958433762,0.006416557774655943,0.004401586658393946,0.003275582990677884],[0.1388853628149074,0.13670793099344228,0.13408460185822582,0.13094509791332462,0.1272114029434128,0.12279675421115506,0.11760444847222372,0.11152682401662711,0.10444520788508493,0.09623217785594207,0.0867580758687681,0.07590414370856197,0.06358481867594341,0.04978212988478095,0.034600093138545264,0.018404201507241574,0.004708851935980792,0.017450539606249427,0.03387053630353306,0.04933437712625864,0.0633175335675311,0.07556384636418222,0.08594425285071317,0.09440956246883611,0.10095984218909376,0.1056219726508368,0.10843359851665864,0.10943280748359861,0.10865319445383069,0.10612418313727583,0.10187670814745158,0.09595463800996037,0.08843268420564501,0.07944210469128433,0.06920657596340295,0.058092950425446634,0.046686760245899774,0.03590876871351437,0.02714664954752809,0.021973887005656674,0.020430557234259905,0.02010509137236442,0.019046685787431825,0.017463669851613225,0.016338621640834536,0.015348841848311066,0.013487594082378986,0.010942108856309205,0.008908563811212767,0.007627374392722962],[0.13926943134017358,0.1371753697250889,0.13464576989966015,0.1316087095967435,0.12798322439305404,0.12367812078922173,0.11859076417173606,0.11260628927098962,0.1055980783996207,0.09743083506162332,0.08796803551641713,0.07708579397873748,0.06469506810362993,0.050773730361128776,0.03541056372206102,0.018877840359133435,0.0028445924564589253,0.016372099051513576,0.03313013513512128,0.048776166517249565,0.06289276633978026,0.0752473918387657,0.08572059019228874,0.09426904711112086,0.10089754577935459,0.10563742514901364,0.10853098043143265,0.10962148021998722,0.10894858593869103,0.10654912509958378,0.10246340674801953,0.09674758690096767,0.08949303858209265,0.08085436809845456,0.07108886188840026,0.06061189655346245,0.050073422429800236,0.04044451232735814,0.032994497014018596,0.02873425806377384,0.02720886502884385,0.02653604841553831,0.025330302230593828,0.023667116808865768,0.022138737289314554,0.02055504492805502,0.018331158812607273,0.01569321860842868,0.01351089318096421,0.012151887430813335],[0.13963752680527566,0.13762268510230607,0.13518223087512096,0.13224296107237385,0.1287216399348803,0.12452376926021742,0.11954252336970377,0.11365838396259649,0.10674039667329913,0.09865043228984628,0.08925230633996127,0.07842806725006879,0.06610452443588016,0.05229616026460316,0.037188258127010536,0.021431110733079812,0.009360489873444705,0.018083602320739724,0.03375976729991973,0.04907864412567228,0.06306328425393022,0.0753637948670726,0.08582246025140187,0.09438085012474037,0.10103770453296969,0.1058227691440349,0.10877945294781304,0.10995419917352826,0.10939177881330049,0.10713626378198646,0.10323782483979903,0.0977658966394011,0.09082973767072258,0.08260804123510761,0.07338993767330171,0.06362946917276542,0.05400897240330555,0.045471868704886426,0.03907374778847204,0.035398562009658886,0.03383109570054922,0.03288928998436195,0.03152844593769089,0.029736794824094016,0.027879430317854264,0.02584918565425507,0.023321939915293466,0.020547868299230103,0.01822891403760018,0.01684185859729759],[0.139990277856573,0.13805101535427597,0.13569587113541404,0.13285079169489278,0.12943100959959264,0.125339891731142,0.12046816379000366,0.11469413635782566,0.10788595093407016,0.09990735295937213,0.09062910091097942,0.07994905468406273,0.06782633617803983,0.05434362972545054,0.039852559310226146,0.02551061779840091,0.01622997128114702,0.02199494360221516,0.03571635749635242,0.050244286228276355,0.06383610108774986,0.07591894739143208,0.0862539152070705,0.09474729064238017,0.10138107209937217,0.1061772541875251,0.10917666775563899,0.11042673117956832,0.10997611313448184,0.1078756057544415,0.10418517076358057,0.09898761573154871,0.09240981727744718,0.08465278126779956,0.07603161757142554,0.0670235912366178,0.0583094700225493,0.05075236860891002,0.04518281341779487,0.04189981092766017,0.04026815986036737,0.03910516502510113,0.03759099578585947,0.03565685963944245,0.033526975529237946,0.031151946654515997,0.02838023483414786,0.025482850047717488,0.02307298436111175,0.021696212184360603],[0.14032845005218236,0.13846162911409238,0.13618867046667635,0.13343514601659537,0.1301155299368872,0.12613222854619005,0.12137521217515478,0.11572296514104015,0.10904588272987695,0.10121379249485735,0.09211007472748899,0.08165637682228694,0.06985595698160206,0.05687730285224301,0.04325375597417531,0.03051322332159478,0.023126020384120698,0.027156745443417275,0.03879109349334996,0.05221084214287913,0.06518734949067796,0.07690182430544334,0.08700884168198258,0.09536414613508049,0.10192393282851621,0.10669687743815588,0.10971772369496052,0.111032646444259,0.11069283706889119,0.10875496933979158,0.10528820593117123,0.10038799506437987,0.09419727480596916,0.08693567496783856,0.0789360116063626,0.07068206263662724,0.06282546857300171,0.056123770031638896,0.051209077366028775,0.04820049881006271,0.04649960048134898,0.045150576862147615,0.04349151418406964,0.04141829202250343,0.03906619450095093,0.03642848553667042,0.033472240230706274,0.030487605084358813,0.028037666597736908,0.026699732088033598],[0.1406528984591452,0.13885586106295705,0.13666261718741016,0.13399886549545462,0.1307791013186166,0.12690591335126933,0.12227011398072879,0.11675250715470353,0.11022853643339221,0.10257767574079443,0.09370042341481262,0.08354779844607488,0.07217349880061415,0.059834729165561304,0.04721914613445385,0.03602097789322708,0.029972582605378197,0.03293252614251703,0.042706182281132384,0.054868620163031775,0.06706674919318148,0.07828601016241343,0.08807161183471542,0.09622099403061321,0.10265832622176985,0.10737457143172423,0.11039536231689202,0.11176355804614764,0.11153143292789772,0.10976045985751087,0.10652797101377127,0.10194063568828372,0.09615491992612303,0.0894042050462334,0.0820299516529236,0.07450747603995919,0.0674408726280053,0.06147660583498668,0.057085621404193244,0.05427742440095979,0.052510914553541156,0.051005138501300874,0.04921461582159638,0.047015911486213396,0.04448883345028409,0.04165924903237452,0.03857720863696356,0.03554903697177443,0.03310518248195469,0.03182619453808555],[0.14096452505393434,0.13923505569087619,0.137119636332387,0.13454460048224767,0.13142522562294376,0.12766536249816668,0.12315812686334571,0.1177885372994234,0.11143944578358553,0.10400278959965367,0.09539934289009783,0.08561249672918313,0.07474725906018033,0.06314048342483661,0.05158515915726356,0.041776625588632654,0.03671918522771375,0.03897582941876693,0.04719705170800906,0.05808438436550619,0.0694053143953923,0.08003268461621242,0.08941844300660257,0.09730192797690292,0.10357248534734169,0.10820052301683519,0.11120024942933394,0.11260942108612639,0.11247998491117751,0.11087696830137447,0.10788450381910687,0.10361855455479593,0.09824595858735528,0.09200849226372304,0.08524764809173134,0.07841854493810226,0.07206781829757379,0.06673683612186239,0.06277111959811578,0.06011594118057609,0.058292219990699286,0.05665595752473981,0.0547511020111904,0.052446699580920776,0.049789307232851465,0.04683014776931868,0.04367739603304575,0.04064909277564217,0.038249538028228176,0.03704266595040223],[0.1412642415709631,0.1396005198174157,0.13756153142377328,0.1350747426166225,0.13205693373677094,0.12841420710441792,0.1240432745420769,0.11883497426674215,0.11268144519939721,0.1054891035943475,0.09720078102306536,0.08783276691507098,0.0775376867938092,0.06671537782838977,0.0562118186374727,0.047620589129344804,0.04332603609713551,0.04509541720552513,0.05204793416573981,0.061722303723396967,0.07212402084574258,0.08209441396833991,0.09101923803743696,0.09858655333749823,0.10465144162661097,0.10916259477687751,0.1121213211740823,0.11355887130541167,0.1135255653437869,0.11208866269723507,0.1093375050780622,0.1053951065111952,0.10043523794570491,0.09470279879553506,0.08853191440158638,0.08234936399470673,0.07664094549530308,0.07185434291150587,0.06823980134475063,0.06570722193602047,0.0638373524737746,0.06209510802467727,0.06009556452147932,0.05770875219956575,0.0549628375346434,0.05192881596838431,0.04875494177263415,0.045765586651072915,0.043440083405628126,0.04231304433392844],[0.1415529381759265,0.13995348413589245,0.13798993980436736,0.13559137704660923,0.13267674133035198,0.12915526466658753,0.12492835538524297,0.1198939619319702,0.11395488650224898,0.10703323769350899,0.09909438567814612,0.09018592247697575,0.08050115130111332,0.07048303695318142,0.0609855553801484,0.053449331540634346,0.0497608220468053,0.05117778833213575,0.05709516477720215,0.0656574169101773,0.0751415001621611,0.08441905623497438,0.0928396365385002,0.10005114325436894,0.10587773635708504,0.11024681411973847,0.11314617033144132,0.11459958241230885,0.11465461797255903,0.11337944690040842,0.11086692127540247,0.10724472940453725,0.10269013963763486,0.0974463851469626,0.09183438612100561,0.08624771068640795,0.08111235986757416,0.07679547970790918,0.07347601449352638,0.0710466974147494,0.06914315769678261,0.06731815697742212,0.06524501609758895,0.0628006429878657,0.06000463143409104,0.056943213254526164,0.05379123514502249,0.05087380359830608,0.048644284934383615,0.047600667839229255],[0.14183145809560183,0.14029507370389327,0.13840630104585205,0.13609625326567815,0.13328663051346604,0.12989054592096222,0.12581499823421136,0.12096601323679855,0.11525793672481767,0.1086290292499623,0.10106654748374234,0.09264617055552733,0.08359310356157411,0.07437381944429261,0.0658167204929664,0.05919253728836546,0.05599742594951634,0.05715063015440801,0.06221823703832858,0.06978188712550942,0.07837973964273538,0.08695323902160207,0.09484302793131144,0.10166983591569816,0.10723217669895857,0.11143789368248658,0.11426144840876784,0.1157186227226711,0.1158533203011131,0.11473336845785062,0.11245342687900811,0.1091435037600035,0.10498115003649734,0.10020385910632784,0.09511511494187379,0.09007305389714435,0.08544758555321573,0.0815382002119216,0.07847103966504006,0.07613303506696056,0.07420890714616132,0.07232320073504225,0.0701980508217874,0.06772107849319535,0.06490959690970138,0.06186124836184451,0.0587672099482448,0.05594808781227131,0.05382975260620072,0.0528701203970334],[0.14210057811884752,0.14062628700940866,0.1388118375564809,0.13659077285311394,0.13388805431105444,0.13062129172868162,0.1267037566702687,0.12205020152115931,0.11658693031912645,0.11026814969033452,0.10310144438671953,0.09518629985606358,0.08677046022827292,0.07832666572729648,0.07063556020943328,0.06480081974917072,0.06201513308602183,0.06296543893849037,0.06732924310887084,0.07400637365283724,0.08176763100698607,0.08964510628159736,0.09699234004336872,0.10341577131889124,0.10869457949671446,0.11271974928612533,0.11545326124717131,0.11690279454575288,0.11710791127942127,0.11613496423072427,0.1140787999808301,0.11106953666761969,0.1072821585563469,0.10294515930559807,0.09834182467790113,0.09379461299009077,0.08962243310841927,0.08606879844430701,0.08322108764240646,0.08096740634181229,0.07903581082200989,0.07711019618019758,0.07495432108053057,0.07246875716775257,0.06967235156033788,0.06667086338034203,0.06366393368155128,0.06096315684578438,0.05896564467042325,0.058088411821165746],[0.1423609946991151,0.14094798300022793,0.13920754620478676,0.1370759920193484,0.1344819604213655,0.1313480341778824,0.12759423223967667,0.12314438362464206,0.11793674930175357,0.11194072583424057,0.10518201415173059,0.09777908508372037,0.08999322056779308,0.08228956654359497,0.0753882955873398,0.07023885666525166,0.06779800616332168,0.06858873449537763,0.07236416993424132,0.07825882187783305,0.08524272521473582,0.0924462509888564,0.09925149553434083,0.10526209414656659,0.11024445767505857,0.11407598728589965,0.11670753970613716,0.11813894344930706,0.11840497525129177,0.11756953887994676,0.11572619443545057,0.11300319085069248,0.10957054268020375,0.10564529750589835,0.10148902233500998,0.09738961635407753,0.09362060719214965,0.09037966598573005,0.08772596283196817,0.08555293005831188,0.08362661327263,0.08168048472304139,0.0795142187123318,0.07704236255923083,0.07428738401302563,0.0713603065556383,0.06846321808874795,0.06589508592620102,0.06402358215127026,0.06322569249069014]],[],[],[[0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182,0.7804676160766182],[0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585,0.7765843425312585],[0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293,0.7724595600294293],[0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999,0.7681218124942999],[0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343,0.7636103240939343],[0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193,0.7589753696755193],[0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056,0.7542779462479056],[0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972,0.7495885650365972],[0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717,0.7449850639400717],[0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515,0.7405494866618515],[0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399,0.7363642667533399],[0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049,0.7325081200191049],[0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645,0.729052061728645],[0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263,0.7260556907936263],[0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822,0.7235632603382822],[0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116,0.7215981591701116],[0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276,0.7201535108086276],[0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566,0.7191776252355566],[0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838,0.7185663876077838],[0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413,0.7181808243352413],[0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883,0.7178737733057883],[0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487,0.717510365834487],[0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244,0.7169822782399244],[0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967,0.7162178242185967],[0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182,0.7151895442417182],[0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946,0.7139204970568946],[0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908,0.7124900674789908],[0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621,0.7110397531638621],[0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875,0.7097790515484875],[0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724,0.7089912024663724],[0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818,0.7090381119954818],[0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375,0.7103632404078375],[0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902,0.7134905214784902],[0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718,0.7190164154341718],[0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452,0.7275908848554452],[0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782,0.7398812934106782],[0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677,0.7565107931408677],[0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653,0.7779594663162653],[0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938,0.8044120330589938],[0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717,0.8355299524545717],[0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441,0.8701184675770441],[0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741,0.9057284180911741],[0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392,0.9388062237532392],[0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533,0.9657734196907533],[0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612,0.9843932930100612],[0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125,0.9948098347981125],[0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578,0.9990941681346578],[1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827,1.0000420949557827],[1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136,1.0000370981543136],[0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836,0.9999480885903836]],[[0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392,0.13818195235221392],[0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628,0.13584903258978628],[0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993,0.1330504842896993],[0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698,0.12971946824928698],[0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763,0.12578437837681763],[0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065,0.12116850489372065],[0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026,0.1157893211577026],[0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673,0.10955760591753673],[0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256,0.10237712058913256],[0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935,0.09414638085999935],[0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134,0.0847652297715134],[0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663,0.07415059719075663],[0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371,0.06226917618729371],[0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995,0.049206135768529995],[0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706,0.035345243037313706],[0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427,0.022107391314347427],[0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146,0.0157284449228146],[0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684,0.023973638313615684],[0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754,0.037866786420506754],[0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766,0.052103230628612766],[0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213,0.06533429606903213],[0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487,0.07705981712878487],[0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659,0.08705402913212659],[0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384,0.09521964924293384],[0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128,0.10152825874008128],[0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674,0.1059873367236674],[0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463,0.10861968166337463],[0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099,0.10945078909165099],[0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147,0.10850249334286147],[0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737,0.10579216786216737],[0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518,0.10133725723707518],[0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712,0.09516521995916712],[0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852,0.0873291913299852],[0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244,0.07792986650999244],[0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138,0.06714431567549138],[0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724,0.055262946059135724],[0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149,0.04273784765983149],[0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953,0.030255234652516953],[0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758,0.018893660510350758],[0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218,0.01065398237074218],[0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869,0.00850379906607869],[0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057,0.009359079402858057],[0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058,0.008482356957472058],[0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688,0.006534241004042688],[0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112,0.006615880870694112],[0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736,0.0075453618847642736],[0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948,0.006572341546405948],[0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024,0.0037110930435627024],[0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421,0.001259864888700421],[0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026,0.0008478723760867026]],[],[]]},{"xaxis.title":"gamma","xaxis2.title":"gamma","xaxis.range":[-6.0,3.0],"xaxis2.range":[-6.0,3.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.29,"yanchor":"middle"},{"buttons":[{"args":[{"visible":[false,false,false,false,true,true,true,true]},{"yaxis.title":"gamma","yaxis.range":[-6.0,3.0],"yaxis2.range":[-6.0,3.0],"yaxis.type":"log","yaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.43,"yanchor":"middle"}],"xaxis":{"anchor":"y","autorange":false,"domain":[0.05,0.45],"exponentformat":"e","range":[-9.0,1.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis":{"anchor":"x","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,3.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"gamma"},"type":"log"},"xaxis2":{"anchor":"y2","autorange":false,"domain":[0.6,1],"exponentformat":"e","range":[-9.0,1.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis2":{"anchor":"x2","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,3.0],"tickfont":{"size":11},"tickmode":"auto","type":"log"},"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Expected Improvement (EI)

In [92]:
ax_client = create_svc_client(botorch_acqf_class=ExpectedImprovement)
for i in range(10):
    parameterization, trial_index = ax_client.get_next_trial()
    ax_client.complete_trial(
        trial_index=trial_index, raw_data=evaluate_svc(parameterization)
    )
results_svc["EI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 09:43:29] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 09:43:29] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='C', parameter_type=FLOAT, range=[1e-09, 10.0], log_scale=True), RangeParameter(name='gamma', parameter_type=FLOAT, range=[1e-06, 1000.0], log_scale=True)], parameter_constraints=[]).
[WARNING 08-11 09:43:32] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [93]:
model = cast(
    TorchModelBridge,
    not_none(ax_client.generation_strategy.model),
)
fig = interact_contour_plotly(model=model, metric_name="accuracy")
fig.update_layout(dict(width=None, autosize=True))
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="b4d54eaf-cb24-4c41-aa54-a4a52140062b" class="plotly-graph-div" style="height:450px; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("b4d54eaf-cb24-4c41-aa54-a4a52140062b")) {                    Plotly.newPlot(                        "b4d54eaf-cb24-4c41-aa54-a4a52140062b",                        [{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x","y":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"yaxis":"y","z":[[1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272],[1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361],[1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279],[1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116],[1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185],[1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903],[1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073],[1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375],[1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043],[1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154],[0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698],[0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619],[0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228],[0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051],[0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845],[0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144],[0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483],[0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799],[0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551],[0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027],[0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524],[0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195],[0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622],[0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693],[0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657],[0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875],[0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377],[0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185],[0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081],[0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204],[0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793],[0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531],[0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512],[0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492],[0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542],[0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954],[0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604],[0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097],[0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726],[0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072],[0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809],[0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588],[0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424],[0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524],[0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346],[0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422],[0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673],[0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234],[0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624],[0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x2","y":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"yaxis":"y2","z":[[0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174],[0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792],[0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367],[0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826],[0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901],[0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781],[0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764],[0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774],[0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058],[0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846],[0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659],[0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415],[0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304],[0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659],[0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288],[0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746],[0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415],[0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906],[0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842],[0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628],[0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315],[0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778],[0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709],[0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697],[0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864],[0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898],[0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102],[0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027],[0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562],[0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063],[0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722],[0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407],[0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152],[0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283],[0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782],[0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274],[0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344],[0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144],[0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788],[0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183],[0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616],[0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294],[0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037],[0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744],[0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468],[0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374],[0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368],[0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438],[0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896],[0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.328092\u003cbr\u003egamma: 1000","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 10\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1.69308e-09\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 3.85096e-06\u003cbr\u003egamma: 1000","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 6.25486e-08\u003cbr\u003egamma: 1000","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1e-09\u003cbr\u003egamma: 344.751"],"visible":false,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],"xaxis":"x","y":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.328092\u003cbr\u003egamma: 1000","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 10\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1.69308e-09\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 3.85096e-06\u003cbr\u003egamma: 1000","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 6.25486e-08\u003cbr\u003egamma: 1000","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1e-09\u003cbr\u003egamma: 344.751"],"visible":false,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],"xaxis":"x2","y":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],"yaxis":"y2","type":"scatter"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x","y":[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],"yaxis":"y","z":[[0.79348965166324,0.7931810251756211,0.7928866152922683,0.7926067000898634,0.7923415445963937,0.792091400196117,0.79185650406231,0.7916370786204158,0.7914333310440931,0.7912454527865308,0.7910736191492359,0.7909179888903229,0.7907787038741421,0.7906558887638677,0.7905496507584443,0.7904600793750481,0.7903872462779746,0.7903312051546034,0.7902919916388355,0.7902696232821301,0.7902640995720084,0.7902754019976309,0.7903034941618035,0.7903483219385196,0.7904098136749134,0.7904878804362774,0.7905824162925909,0.7906932986448155,0.7908203885890432,0.7909635313164268,0.7911225565466934,0.7912972789929252,0.7914874988552022,0.7916930023406286,0.791913562207216,0.792148938329063,0.792398878280259,0.7926631179349503,0.7929413820810222,0.7932333850448982,0.7935388313250056,0.793857416231525,0.7941888265301207,0.7945327410874354,0.7948888315162328,0.7952567628181721,0.7956361940223138,0.7960267788175643,0.796428166177393,0.7968400009752666],[0.7873152101697144,0.7869631030094115,0.7866270508127711,0.7863073864505195,0.7860044274619257,0.7857184752876802,0.7854498145370845,0.7851987122932951,0.7849654174602225,0.7847501601544982,0.7845531511457073,0.7843745813478369,0.7842146213646043,0.7840734210910294,0.783951109373276,0.7838477937284385,0.7837635601255799,0.7836984728289409,0.7836525743038548,0.7836258851855076,0.7836184043102852,0.7836301088090746,0.7836609542614985,0.7837108749097115,0.7837797839300387,0.7838675737604233,0.7839741164813502,0.7840992642476545,0.7842428497683819,0.7844046868316699,0.7845845708714456,0.7847822795725989,0.7849975735111873,0.7852301968261549,0.785479877919011,0.7857463301778994,0.7860292527225154,0.786328331166364,0.7866432383929296,0.7869736353424125,0.7873191718058028,0.7876794872231845,0.7880542114833069,0.7884429657216112,0.7888453631140616,0.7892610096643015,0.7896895049818227,0.7901304430490186,0.7905834129751621,0.7910479997355286],[0.780885756309152,0.7804855935379387,0.7801034684157527,0.7797397786324787,0.7793949039693798,0.7790692053064188,0.7787630236714616,0.7784766793368024,0.7782104709682618,0.7779646748318748,0.7777395440628841,0.7775353080014046,0.7773521715987138,0.7771903148976762,0.7770498925903051,0.7769310336549397,0.7768338410749447,0.7767583916402635,0.7767047358325485,0.776672897793998,0.7766628753794205,0.7766746402904683,0.7767081382904042,0.7767632894972348,0.77683998875253,0.7769381060627863,0.7770574871097731,0.7771979538259255,0.7773593050305363,0.7775413171222305,0.7777437448230005,0.7779663219689283,0.7782087623426189,0.7784707605423223,0.778751992882726,0.7790521183224428,0.7793707794133105,0.7797076032667434,0.7800622025325381,0.7804341763857203,0.7808231115172303,0.7812285831244747,0.7816501558980204,0.7820873850009518,0.782539817037685,0.7830069910092894,0.7834884392526338,0.7839836883609363,0.7844922600835534,0.7850136722030892],[0.7742744687750402,0.7738216775047821,0.7733890316921657,0.7729770053080411,0.7725860515652336,0.7722166016289759,0.7718690633774352,0.7715438202203391,0.7712412299835063,0.7709616238667907,0.7707053054825471,0.7704725499812308,0.7702636032701476,0.770078681330694,0.7699179696386675,0.7697816226914012,0.7696697636445962,0.7695824840608055,0.7695198437705784,0.769481870846317,0.7694685616879609,0.7694798812186802,0.7695157631878905,0.7695761105780615,0.7696607961110359,0.7697696628488848,0.769902524883725,0.7700591681104072,0.7702393510755736,0.7704428058962557,0.770669239240957,0.7709183333660357,0.7711897472001503,0.7714831174695709,0.7717980598572696,0.77213417018888,0.7724910256388562,0.7728681859504432,0.7732651946634042,0.773681580343806,0.774116857810547,0.7745705293537173,0.7750420859402816,0.775531008402992,0.7760367686088461,0.7765588306037995,0.77709665173084,0.777649683718892,0.778217373740383,0.7787991654356355],[0.7675764461351676,0.7670666535460815,0.7665792068568742,0.7661146691690661,0.7656735797751018,0.7652564524768478,0.7648637739617568,0.7644960022486547,0.7641535652149687,0.7638368592168882,0.7635462478134444,0.763282060604811,0.7630445921942584,0.7628341012821678,0.7626508098993177,0.7624949027853449,0.7623665269168568,0.762265791188161,0.7621927662460379,0.7621474844784072,0.7621299401551942,0.762140089718211,0.7621778522154448,0.7622431098738452,0.7623357088035305,0.7624554598253026,0.7626021394125126,0.7627754907376236,0.7629752248133105,0.7632010217176022,0.7634525318923948,0.7637293775046555,0.7640311538597644,0.7643574308567005,0.7647077544751437,0.7650816482850271,0.7654786149696069,0.765898137853713,0.7663396824294689,0.7668026978724309,0.7672866185417604,0.7677908654587097,0.7683148477583523,0.7688579641101223,0.7694196041033294,0.7699991495943904,0.7705959760130479,0.771209453625343,0.7718389487515658,0.7724838249378163],[0.7609103307914745,0.7603396402406062,0.759793539059954,0.7592726934357739,0.7587777426472408,0.7583092968677506,0.7578679350275607,0.7574542027558647,0.7570686104205114,0.7567116312833873,0.7563836997889462,0.7560852100024886,0.7558165142135534,0.7555779217182089,0.7553696977921314,0.7551920628641843,0.7550451918978055,0.754929213984933,0.7548442121545241,0.7547902233950173,0.7547672388874256,0.7547752044432088,0.7548140211387124,0.7548835461358407,0.7549835936767938,0.7551139362391867,0.7552743058366838,0.7554643954494482,0.7556838605682044,0.7559323208355349,0.7562093617681481,0.7565145365442267,0.75684736784057,0.7572073497050273,0.7575939494506484,0.7580066095590081,0.7584447495812706,0.7589077680266887,0.7593950442293846,0.7599059401853812,0.7604398023529396,0.7609959634102981,0.7615737439658693,0.7621724542168544,0.7627913955530441,0.7634298621033181,0.7640871422230117,0.7647625199208935,0.7654552762250125,0.766164690487103],[0.7544187173673151,0.7537840821221494,0.7531762519997959,0.752596010584911,0.7520441117055293,0.7515212765578119,0.7510281908843,0.7505655022331053,0.750133817326474,0.7497336995676148,0.7493656667145091,0.7490301887485415,0.7487276859641783,0.7484585273035493,0.7482230289567154,0.7480214532446482,0.7478540077976807,0.7477208450374748,0.7476220619656205,0.7475577002569754,0.7475277466509661,0.7475321336294914,0.7475707403659315,0.7476433939262108,0.7477498706999854,0.7478898980378594,0.7480631560691169,0.7482692796737447,0.7485078605824764,0.7487784495791338,0.7490805587805813,0.7494136639710525,0.7497772069693532,0.7501705980093925,0.7505932181165604,0.7510444214645831,0.7515235376995666,0.7520298742199578,0.7525627184030447,0.7531213397703752,0.7537049920860746,0.7543129153834651,0.7549443379166575,0.7555984780348683,0.7562745459781615,0.7569717455940841,0.7576892759753326,0.7584263330190959,0.759182110909156,0.7599558035221443],[0.7482665801784887,0.7475662940776651,0.7468949060539388,0.746253330126408,0.7456424484708427,0.7450631076848799,0.7445161150707651,0.7440022349761225,0.7435221852368088,0.7430766337686456,0.7426661953564659,0.7422914286891704,0.7419528336881318,0.7416508491731715,0.7413858509054081,0.7411581500396153,0.7409679920105663,0.740815555868513,0.7407009540689244,0.7406242327114108,0.7405853722129199,0.7405842883913374,0.7406208339279464,0.7406948001711345,0.7408059192394225,0.7409538663793774,0.7411382625331562,0.7413586770711281,0.7416146306469905,0.7419055981357384,0.7422310116184838,0.7425902633821853,0.742982708906593,0.7434076698149505,0.7438644367690684,0.7443522722931873,0.7448704135145064,0.7454180748113217,0.745994450362395,0.7465987165934524,0.7472300345186103,0.7478875519760849,0.7485704057587773,0.7492777236412903,0.7500086263056512,0.7507622291685305,0.7515376441130903,0.7523339811287952,0.7531503498626116,0.7539858610850206],[0.7426366755376367,0.7418709913445163,0.7411360563185783,0.740432923366489,0.7397626130157059,0.739126108672709,0.7385243518037766,0.7379582370915604,0.7374286076307074,0.7369362502353775,0.7364818909398939,0.7360661907799625,0.7356897419448184,0.7353530643893242,0.73505660298868,0.7348007253067012,0.7345857200318688,0.7344117961144739,0.7342790826147287,0.7341876292476213,0.7341374075875816,0.7341283128765355,0.7341601663639642,0.7342327180978712,0.7343456500811114,0.7344985797078718,0.7346910633993201,0.734922600364516,0.7351926364215479,0.7355005678235798,0.7358457450443077,0.7362274764866834,0.736645032087307,0.7370976467964077,0.7375845239197654,0.7381048383142701,0.738657739433142,0.7392423542202496,0.7398577898555747,0.7405031363557841,0.7411774690352204,0.7418798508334887,0.7426093345163005,0.7433649647564238,0.7441457801015312,0.7449508148355162,0.7457791007394967,0.7466296687582857,0.7475015505776299,0.748393780117005],[0.7377205701810938,0.7368924225078552,0.7360965005774196,0.7353339940434169,0.7346060620482994,0.7339138275383214,0.7332583713177933,0.7326407258882839,0.732061869138521,0.7315227179748204,0.7310241220092086,0.7305668574510331,0.7301516213743102,0.7297790265523196,0.7294495970570171,0.7291637648081227,0.7289218672221348,0.7287241460562849,0.728570747473049,0.7284617232777548,0.7283970332166474,0.7283765481747784,0.7284000540867905,0.7284672563685723,0.7285777846895404,0.7287311979280234,0.7289269891801109,0.7291645907208831,0.7294433788432914,0.7297626785226027,0.7301217678728402,0.7305198823761744,0.7309562188772616,0.7314299393426418,0.7319401743910925,0.7324860266047721,0.7330665736335122,0.7336808711060602,0.7343279553626958,0.7350068460236654,0.7357165484074396,0.736456055812051,0.7372243516717827,0.7380204116003617,0.7388432053306062,0.7396916985592447,0.740564854704407,0.741461636582118,0.7423810080070177,0.7433219353215341],[0.7337037942651832,0.7328194964791169,0.7319684124582961,0.7311518477231854,0.7303710813640804,0.7296273599081092,0.7289218907322724,0.7282558350163431,0.7276303002423707,0.7270463322695835,0.7265049070501118,0.7260069221095791,0.7255531880050131,0.7251444200934529,0.7247812310839771,0.7244641249587869,0.7241934928599578,0.7239696113802943,0.7237926433780757,0.7236626410688263,0.7235795508800983,0.723543219464408,0.7235534003241302,0.7236097606327356,0.7237118879730254,0.7238592968227529,0.7240514346950816,0.724287687891304,0.7245673868541141,0.7248898111282384,0.7252541939460208,0.725659726461634,0.7261055616607693,0.7265908179740201,0.7271145826223797,0.727675914722688,0.7282738481797395,0.7289073943902362,0.7295755447819472,0.7302772732094012,0.7310115382252342,0.7317772852440321,0.7325734486131634,0.7333989536027916,0.7342527183249804,0.7351336555896794,0.7360406747033617,0.73697268321429,0.737928588606779,0.7389072999454547],[0.7307443496353783,0.7298138622794049,0.7289170457231668,0.7280552796300388,0.727229920912652,0.7264422976449804,0.725693702477975,0.7249853855285648,0.7243185467103723,0.7236943274730441,0.7231138019157332,0.7225779672393496,0.7220877335030448,0.7216439126594698,0.7212472068986321,0.7208981966723601,0.7205973303779589,0.7203449204722256,0.7201411482647939,0.7199860732017944,0.7198796427544221,0.7198217017718641,0.7198120011295037,0.7198502056792169,0.719935901537789,0.7200686027549393,0.7202477574034594,0.7204727531339787,0.7207429222366537,0.7210575462517388,0.7214158601706019,0.7218170562681889,0.7222602876072213,0.7227446712534165,0.7232692912397297,0.7238332013159559,0.7244354275179777,0.725074970588495,0.7257508082782116,0.7264618975532594,0.7272071767311399,0.7279855675637709,0.7287959772824313,0.7296373006156326,0.7305084217873036,0.7314082164993019,0.7323355538992146,0.7332892985317951,0.7342683122702274,0.7352714562217368],[0.7289474710748803,0.7279835232369231,0.7270532003763259,0.7261579055131685,0.7252990199203676,0.7244778970465452,0.7236958559394147,0.7229541741396673,0.7222540800147315,0.7215967445022826,0.7209832722367263,0.720414692042657,0.719891946810478,0.7194158828576477,0.7189872391190995,0.7186066370729068,0.7182745731944908,0.717991416087732,0.7177574090262736,0.7175726764312041,0.7174372321067104,0.7173509877776312,0.7173137612791907,0.717325284172762,0.7173852087302869,0.7174931142919174,0.7176485130246397,0.7178508551190927,0.7180995334662935,0.7183938878585935,0.7187332087610507,0.7191167407008396,0.7195436853233919,0.720013204164575,0.7205244211882151,0.7210764251374744,0.7216682717468602,0.722298985858824,0.7229675634849833,0.72367297384699,0.7244141614261214,0.7251900480440208,0.7259995349899862,0.7268415052031414,0.7277148255111113,0.7286183489207967,0.7295509169517467,0.7305113619986741,0.7314985097068845,0.7325111813428],[0.7283471006331083,0.7273630565638114,0.7264120965814371,0.7254955961101005,0.7246149073665383,0.7237713533731732,0.7229662215523153,0.722200756911256,0.7214761548465326,0.7207935536234872,0.7201540266275459,0.7195585745389785,0.7190081176530834,0.7185034886462658,0.7180454261584603,0.7176345695958314,0.7172714555233157,0.7169565158973872,0.7166900782012287,0.7164723673370015,0.7163035089633125,0.7161835338789726,0.7161123830489892,0.7160899129207294,0.7161159007556784,0.7161900497810665,0.7163119940332746,0.7164813028177242,0.7166974847491799,0.7169599913650487,0.717268220325367,0.7176215182291953,0.718019183089716,0.7184604665204282,0.718944575692798,0.7194706751314903,0.7200378884164383,0.7206452998609992,0.7212919562317855,0.7219768685682217,0.7226990141486631,0.7234573386357296,0.7242507584175466,0.7250781631453429,0.7259384184528714,0.7268303688307023,0.7277528406194343,0.7287046450806097,0.7296845815023933,0.7306914402983467],[0.7289059467959619,0.7279138301080764,0.7269537748751317,0.7260270894744489,0.7251350577543169,0.7242789337105728,0.7234599359499816,0.7226792419896644,0.7219379824587122,0.7212372352869296,0.7205780199852958,0.7199612921413051,0.7193879382672342,0.7188587711473096,0.718374525827429,0.717935856375963,0.7175433335153636,0.7171974431834127,0.7168985860340611,0.7166470778368943,0.7164431506878087,0.7162869549068864,0.7161785614759715,0.7161179648587255,0.7161050860484472,0.7161397757008413,0.7162218172269834,0.7163509297430763,0.7165267707961152,0.7167489388070378,0.7170169751948909,0.7173303661671624,0.7176885441832792,0.7180908891209459,0.7185367291988926,0.7190253417342827,0.7195559538368649,0.7201277431616574,0.7207398388527384,0.7213913228073998,0.7220812313689124,0.7228085575178542,0.723572253581971,0.7243712344324909,0.7252043810910317,0.7260705446429385,0.7269685503421685,0.7278972017971619,0.7288552851414216,0.7298415731114799],[0.7305318038037891,0.7295414997202498,0.7285818473791955,0.7276540695408587,0.7267593650269726,0.7258989043885338,0.7250738255119336,0.7242852292101933,0.7235341748531736,0.7228216760970159,0.7221486967781163,0.7215161470399101,0.720924879761008,0.7203756873501751,0.7198692989669022,0.7194063782158363,0.7189875213493915,0.7186132559961866,0.7182840404145704,0.7180002632516772,0.7177622437705243,0.7175702324918176,0.7174244121843003,0.7173248991282379,0.717271744571127,0.7172649362927905,0.7173044001982224,0.7173900018602657,0.7175215479398553,0.7176987874185483,0.7179214125860638,0.7181890597345066,0.7185013095213063,0.7188576869760028,0.7192576611446638,0.7197006443952516,0.7201859914565554,0.7207129983437419,0.7212809014404655,0.7218888771369243,0.7225360424869836,0.7232214572410249,0.723944127319807,0.7247030094671111,0.7254970166403765,0.7263250237118106,0.7271858731686803,0.7280783806251081,0.7290013400475619,0.7299535286507761],[0.733097644601595,0.7321168294404261,0.73116501082566,0.730243323633461,0.7293528809602715,0.7284947707192244,0.7276700522428956,0.7268797529250368,0.7261248649361121,0.7254063420488654,0.7247250966105896,0.7240819966980478,0.7234778634890008,0.7229134688809034,0.7223895333825973,0.7219067242987761,0.7214656542198532,0.7210668798218669,0.7207109009725465,0.7203981601310102,0.7201290420201492,0.7199038735429565,0.7197229239071499,0.7195864049166961,0.7194944713843793,0.7194472216164335,0.719444697918448,0.719486887071141,0.71957372072503,0.7197050756643146,0.7198807738922219,0.7201005824924441,0.7203642132239418,0.7206713218091179,0.7210215068780603,0.7214143085340978,0.7218492065082172,0.7223256178719248,0.7228428942798404,0.7234003187169791,0.7239971022336705,0.7246323848803372,0.7253052425340663,0.7260146946257309,0.7267597113825336,0.7275392205832287,0.728352113849331,0.7291972524952066,0.7300734729594154,0.7309795918390736],[0.7364581484348216,0.7354923386270604,0.7345537553810169,0.7336434520443048,0.7327624630472311,0.7319118012262513,0.7310924551733382,0.7303053866318319,0.7295515279596685,0.728831779680727,0.7281470081443406,0.7274980433117382,0.7268856766862968,0.7263106594019996,0.7257737004814355,0.725275465271096,0.7248165740577207,0.7243976008651115,0.7240190724262986,0.7236814673213516,0.7233852152666103,0.7231306965367941,0.7229182414974777,0.7227481302218648,0.7226205921627566,0.7225358058481351,0.7224938985669023,0.7224949460100415,0.7225389718318243,0.7226259470956721,0.7227557895700193,0.7229283628411947,0.7231434752134788,0.7234008783722377,0.7237002657968494,0.7240412709311947,0.7244234651609036,0.7248463557252569,0.7253093838256452,0.7258119233708079,0.7263532809255328,0.7269326973294948,0.7275493510657906,0.728202363012709,0.7288908020047211,0.7296136906954647,0.7303700113915288,0.731158711678602,0.7319787097567485,0.7328288994523987],[0.740461955847344,0.7395144801414337,0.7385924382637657,0.7376968116826096,0.7368285658416679,0.7359886480029167,0.735177985113,0.734397481705497,0.7336480178511184,0.7329304471673314,0.7322455948980839,0.7315942560731554,0.7309771937552355,0.7303951373811101,0.7298487812013688,0.7293387828208391,0.7288657618395812,0.7284302985917623,0.7280329329771591,0.7276741633774606,0.7273544456470471,0.7270741921655651,0.7268337709375139,0.7266335047222579,0.7264736701765182,0.7263544969905726,0.726276166999259,0.7262388132496362,0.7262425190090576,0.7262873167008093,0.7263731867598295,0.7265000564089312,0.7266677983670771,0.7268762295162586,0.7271251095727513,0.7274141398315469,0.7277429620777507,0.7281111577817133,0.728518247709458,0.7289636920792423,0.7294468913731114,0.7299671878684473,0.7305238678954932,0.7311161647652651,0.7317432622618518,0.7324042985629664,0.733098370444612,0.7338245376355388,0.7345818272076389,0.7353692379128194],[0.7449610177045642,0.7440329539067841,0.7431285598381965,0.7422487553706665,0.7413944468966253,0.7405665255195651,0.739765865257829,0.7389933212688745,0.7382497281008142,0.7375358979775013,0.7368526191227487,0.7362006541284475,0.7355807383703805,0.7349935784744528,0.7344398508348678,0.7339202001845296,0.7334352382166497,0.7329855422552416,0.7325716539709335,0.732194078137375,0.7318532814225187,0.7315496912082808,0.7312836944316203,0.7310556364399772,0.7308658198544115,0.7307145034347351,0.7306019009425935,0.7305281800008793,0.7304934609511962,0.7304978157153713,0.7305412666722806,0.7306237855674214,0.7307452924795698,0.7309056548761103,0.7311046867956794,0.7313421482028264,0.7316177445635422,0.7319311266917267,0.7322818909141002,0.7326695795941993,0.7330936820449747,0.7335536358448861,0.7340488285556158,0.734578599822413,0.7351422438224917,0.735739012014389,0.7363681161327422,0.7370287313688332,0.7377199996771764,0.7384410331516138],[0.7498181557736581,0.7489083226204692,0.7480204452241661,0.7471553921242202,0.7463140204680626,0.745497174423966,0.7447056835964421,0.743940361448495,0.7432020037347853,0.7424913869493989,0.7418092667914936,0.7411563766516203,0.7405334261209848,0.739941099525375,0.7393800544849025,0.7388509205001648,0.7383542975649073,0.7378907548048175,0.7374608291417192,0.7370650239822147,0.7367038079297543,0.7363776135192571,0.7360868359737968,0.7358318319835178,0.7356129185079241,0.7354303716039728,0.7352844252840463,0.7351752704098447,0.7351030536305085,0.7350678763758004,0.735069793917828,0.7351088145174729,0.7351848986742074,0.7352979585001377,0.735447857240681,0.7356344089650235,0.7358573784492077,0.7361164812731987,0.7364113841504929,0.7367417055047912,0.7371070163031049,0.737506841148651,0.7379406596304113,0.7384079079196573,0.7389079805975433,0.7394402326924114,0.7400039819010427,0.74059851096492,0.7412230701707152,0.7418768799436251],[0.7549132909762875,0.7540183466874134,0.7531436985527271,0.7522901744390531,0.7514585925274331,0.7506497598649418,0.7498644709109337,0.7491035060807796,0.7483676302900146,0.7476575915016633,0.7469741192793219,0.7463179233483935,0.7456896921676812,0.7450900915133571,0.7445197630771762,0.743979323080668,0.7434693609069754,0.7429904377519896,0.7425430852965076,0.7421278044012934,0.7417450638272038,0.7413952989829171,0.7410789107033282,0.7407962640623098,0.7405476872243135,0.7403334703401707,0.7401538644934376,0.7400090807046855,0.7398992890022216,0.7398246175687951,0.739785151974836,0.7397809345096182,0.7398119636223712,0.7398781934857046,0.7399795336936885,0.7401158491065011,0.7402869598526518,0.740492641498423,0.7407326253923245,0.7410065991900915,0.7413142075631237,0.7416550530903805,0.7420286973307113,0.7424346620695619,0.7428724307310759,0.7433414499439309,0.7438411312469282,0.7443708529184583,0.744929961912562,0.7455177758834025],[0.7601484000641402,0.7592630466582752,0.7583963797405675,0.7575491981994159,0.7567222927244128,0.75591644444197,0.7551324235402441,0.7543709878860314,0.7536328816362929,0.7529188338469622,0.7522295570816755,0.7515657460230621,0.7509280760892325,0.7503172020581264,0.7497337567024218,0.7491783494377766,0.7486515649872774,0.7481539620651086,0.747686072082643,0.7472483978803809,0.7468414124894434,0.7464655579266516,0.74612124402759,0.7458088473224573,0.7455287099599475,0.7452811386848505,0.7450664038755218,0.744884738647793,0.7447363380322984,0.744621358232509,0.7445399159710036,0.7444920879316146,0.7444779103050527,0.7444973784454139,0.7445504466445736,0.7446370280308905,0.7447569945978332,0.7449101773671523,0.7450963666900289,0.7453153126882819,0.7455667258362293,0.7458502776822309,0.7461656017073093,0.7465122943166427,0.7468899159581445,0.747297992360894,0.7477360158848558,0.7482034469721872,0.748699715689498,0.7492242233497124],[0.7654511896099171,0.7645684526441049,0.7637028328716402,0.7628551133545809,0.7620260703968461,0.761216472222514,0.7604270776400042,0.7596586346948387,0.7589118793137583,0.7581875339430487,0.7574863061840205,0.7568088874286717,0.7561559514986587,0.755528153290805,0.7549261274324952,0.7543504869504232,0.7538018219563098,0.7532806983533531,0.7527876565673455,0.7523232103065738,0.7518878453547972,0.7514820184018118,0.751106155916293,0.750760653065816,0.7504458726891315,0.7501621443259496,0.7499097633096146,0.7496889899281658,0.7495000486593248,0.7493431274849462,0.7492183772903924,0.7491259113541355,0.7490658049326465,0.7490380949452893,0.7490427797635031,0.749079819108015,0.7491491340571935,0.7492506071689242,0.7493840827175836,0.7495493670468087,0.7497462290378292,0.7499744006921687,0.7502335778265387,0.7505234208767829,0.7508435558067849,0.7511935751173632,0.7515730389493545,0.7519814762743484,0.752418386165904,0.7528832391435467],[0.7707775619709192,0.7698891120696688,0.7690162358414085,0.7681597152653271,0.7673203271109962,0.766498841622038,0.7656960211823916,0.7649126189680663,0.7641493775874145,0.7634070277130831,0.7626862867089425,0.7619878572554234,0.7613124259768254,0.7606606620742937,0.7600332159682981,0.7594307179545715,0.7588537768776025,0.7583029788259013,0.7577788858533756,0.7572820347312773,0.7568129357352765,0.7563720714723221,0.7559598957520216,0.7555768325073337,0.755223274769401,0.7548995837013593,0.7546060876959341,0.7543430815415714,0.7541108256617453,0.7539095454319358,0.7537394305785694,0.7536006346639584,0.7534932746609742,0.7534174306208201,0.7533731454368573,0.7533604247069579,0.7533792366963497,0.7534295124023379,0.753511145721699,0.7536239937208897,0.7537678770085713,0.7539425802092685,0.754147852536315,0.7543834084615698,0.7546489284787475,0.7549440599565875,0.755268418077514,0.7556215868569104,0.7560031202376599,0.7564125432541963],[0.7761130373955104,0.7752095312945412,0.774320060009308,0.7734454207004782,0.7725864071125884,0.7717438082242409,0.7709184068763297,0.7701109783814646,0.7693222891179431,0.7685530951117916,0.7678041406105698,0.7670761566527946,0.7663698596369999,0.7656859498945945,0.7650251102708259,0.7643880047182856,0.7637752769075096,0.7631875488593326,0.7626254196037474,0.7620894638700858,0.7615802308133943,0.7610982427819085,0.7606439941305312,0.7602179500852035,0.7598205456630076,0.7594521846527569,0.7591132386607208,0.7588040462259777,0.7585249120097113,0.7582761060625338,0.7580578631736717,0.7578703823055386,0.7577138261168904,0.7575883205773817,0.7574939546759342,0.757430780224887,0.7573988117614293,0.7573980265473192,0.7574283646673788,0.7574897292267253,0.7575819866461563,0.7577049670545656,0.7578584647767259,0.7580422389142422,0.7582560140169663,0.758499480841671,0.7587722971943139,0.7590740888517911,0.7594044505586891,0.7597629470941835],[0.7814733225141631,0.7805447564998041,0.7796286616227007,0.7787258678289429,0.7778372038225004,0.7769634956395721,0.7761055651939162,0.7752642287966676,0.7744402956543788,0.7736345663492477,0.7728478313057023,0.7720808692477256,0.7713344456514868,0.7706093111980394,0.7699062002309909,0.769225829224215,0.7685688952647929,0.767936074556479,0.7673280209490693,0.7667453644991088,0.7661887100674016,0.76565863595879,0.7651556926096351,0.7646804013283747,0.7642332530944296,0.7638147074206045,0.7634251912839584,0.7630650981299185,0.7627347869541687,0.7624345814665737,0.76216476934108,0.7619256015552014,0.7617172918223093,0.7615400161195467,0.7613939123137454,0.761279079887273,0.7611955797652454,0.7611434342450543,0.7611226270286371,0.7611331033574081,0.7611747702492386,0.7612474968363608,0.7613511148025447,0.7614854189174062,0.7616501676652087,0.7618450839650545,0.7620698559789265,0.7623241380036234,0.7626075514422508,0.7629196858505969],[0.7869041738245173,0.7859402557958015,0.7849871808947451,0.7840458305465208,0.7831170876406441,0.7822018349835675,0.7813009537115708,0.7804153216678505,0.7795458117480232,0.7786932902185402,0.7778586150128097,0.7770426340100816,0.7762461833024163,0.775470085455298,0.7747151477676637,0.773982160537322,0.7732718953379051,0.7725851033136316,0.7719225134982708,0.7712848311647772,0.7706727362120964,0.7700868815956501,0.7695278918079653,0.7689963614158384,0.7684928536602929,0.7680178991254316,0.7675719944820736,0.7671556013118058,0.7667691450167948,0.7664130138203563,0.7660875578629084,0.7657930883975159,0.7655298770887847,0.7652981554183762,0.7650981141999063,0.764929903205452,0.7647936309053309,0.7646893643222495,0.7646171290003279,0.7645769090889204,0.7645686475405653,0.764592246421801,0.7646475673350259,0.7647344319490059,0.7648526226351012,0.7650018832057695,0.7651819197514111,0.7653924015711797,0.7656329621929553,0.7659032004773113],[0.792480613580007,0.7914711698560708,0.7904708261909579,0.7894805349401943,0.7885012533463065,0.7875339418215416,0.7865795621752739,0.7856390757904499,0.7847134417538218,0.7838036149451363,0.7829105440908374,0.7820351697882295,0.7811784225064061,0.7803412205706048,0.7795244681369602,0.7787290531649249,0.7779558453948833,0.7772056943387045,0.7764794272911641,0.7757778473702944,0.7751017315948175,0.7744518290068468,0.7738288588480275,0.7732335087972148,0.7726664332776537,0.7721282518414391,0.7716195476387796,0.7711408659792887,0.7706927129921471,0.7702755543915716,0.7698898143535313,0.7695358745091387,0.7692140730595514,0.7689247040166096,0.7686680165727775,0.7684442146032533,0.7682534563024181,0.7680958539560383,0.7679714738498994,0.7678803363147955,0.7678224159070428,0.7677976417229486,0.767805897844938,0.7678470239163393,0.7679208158411572,0.7680270266045199,0.7681653672088974,0.7683355077206286,0.7685370784208031,0.7687696710540876],[0.7983054322696919,0.797240871752136,0.7961834906848207,0.7951343320905149,0.7940944482443215,0.7930648987388659,0.792046748472099,0.7910410655624782,0.7900489191968464,0.7890713774169048,0.7881095048507445,0.7871643603964558,0.7862369948653718,0.7853284485930263,0.7844397490263958,0.7835719082964514,0.7827259207854709,0.7819027606989208,0.7811033796520539,0.7803287042816134,0.7795796338932399,0.7788570381552989,0.7781617548498989,0.7774945876918412,0.77685630422613,0.7762476338144761,0.7756692657209415,0.7751218473064982,0.7746059823418199,0.7741222294470755,0.7736711006668701,0.7732530601877655,0.7728685232050507,0.7725178549445695,0.7722013698445278,0.7719193309012421,0.7716719491818086,0.7714593835056485,0.7712817402958545,0.7711390736002139,0.7710313852807537,0.7709586253696248,0.7709206925881501,0.7709174350249042,0.7709486509677801,0.7710140898841472,0.7711134535424142,0.77124639726759,0.7714125313227991,0.7716114224081435],[0.8045067672262114,0.8033786287785655,0.80225549785317,0.8011385274622489,0.8000288854517651,0.7989277523063937,0.7978363188467634,0.7967557838239546,0.7956873514170284,0.7946322286401672,0.7935916226668199,0.7925667380790472,0.7915587740510758,0.7905689214768485,0.7895983600521256,0.7886482553224213,0.7877197557087408,0.7868139895237222,0.7859320619913461,0.7850750522838725,0.7842440105900697,0.7834399552291061,0.7826638698246837,0.7819167005540758,0.7811993534867065,0.780512692026736,0.7798575344738299,0.7792346517158562,0.7786447650666766,0.778088544261502,0.7775666056214358,0.7770795103978622,0.7766277633062526,0.7762118112577653,0.7758320422957201,0.7754887847426637,0.7751823065622873,0.7749128149389907,0.7746804560763487,0.7744853152142257,0.7743274168627546,0.7742067252499161,0.7741231449780038,0.7740765218828889,0.7740666440887025,0.774093243249349,0.7741559959671755,0.774254525378147,0.7743884028920341,0.7745571500754019],[0.811234386244628,0.8100359946237402,0.8088401042255109,0.8076479959270382,0.8064609725498224,0.8052803563738501,0.8041074865033933,0.8029437160893075,0.8017904094136857,0.8006489388438326,0.7995206816636578,0.7984070167917533,0.7973093213965966,0.7962289674205013,0.795167318025111,0.7941257239723859,0.7931055199561416,0.7921080209002671,0.7911345182407346,0.7901862762094163,0.7892645281385244,0.7883704728051425,0.7875052708358559,0.7866700411918311,0.7858658577548754,0.7850937460349924,0.7843546800197103,0.7836495791850232,0.7829793056871043,0.7823446617530536,0.7817463872878206,0.78118515771309,0.7806615820523767,0.7801762012748212,0.7797294869082741,0.7793218399301848,0.7789535899426383,0.7786249946356151,0.7783362395402255,0.7780874380713405,0.7778786318567157,0.7777097913474383,0.7775808167023546,0.7774915389370616,0.7774417213261504,0.7774310610456256,0.777459191040895,0.7775256821043686,0.777630045145592,0.7777717336359402],[0.8186541336798615,0.8173813832220616,0.8161082055199663,0.814836024289952,0.8135662941592879,0.8123004978804164,0.8110401433446595,0.8097867603991323,0.8085418974720142,0.807307118012798,0.806083996755668,0.8048741158157684,0.8036790606297943,0.8025004157540526,0.8013397605348969,0.8001986646682174,0.7990786836664272,0.7979813542531404,0.7969081897074233,0.795860675181105,0.7948402630141312,0.7938483680742839,0.7928863631487411,0.7919555744158877,0.7910572770264553,0.7901926908234513,0.7893629762303827,0.7885692303369821,0.7878124832109648,0.7870936944632807,0.7864137500928549,0.7857734596349655,0.7851735536351605,0.7846146814680313,0.7840974095172399,0.7836222197300038,0.7831895085558204,0.7827995862756182,0.7824526767238321,0.7821489174021716,0.7818883599801487,0.7816709711738535,0.7814966339910391,0.7813651493273787,0.7812762378958631,0.781229542468709,0.7812246304089263,0.7812609964668592,0.7813380658155646,0.781455197297852],[0.826939826689315,0.825592096583529,0.8242405043693074,0.8228866267815068,0.8215320825712662,0.8201785294443896,0.8188276607349831,0.8174812018158533,0.8161409062488325,0.8148085516799753,0.813485935486513,0.8121748701845258,0.8108771786085247,0.809594688876485,0.8083292291563656,0.8070826222527496,0.8058566800349158,0.8046531977304154,0.8034739481109915,0.8023206756004412,0.8011950903367068,0.8000988622230576,0.7990336150055779,0.7980009204163041,0.7970022924231206,0.7960391816288833,0.7951129698630999,0.7942249650098172,0.7933763961150252,0.7925684088158952,0.7918020611324494,0.791078319659803,0.7903980561959356,0.789762044836058,0.7891709595601131,0.788625372334813,0.7881257517460609,0.7876724621716323,0.7872657634978603,0.7869058113778113,0.7865926580222901,0.7863262535090595,0.7861064475900734,0.7859329919713994,0.7858055430359782,0.7857236649754729,0.7856868332943033,0.7856944386465269,0.7857457909645529,0.7858401238377284],[0.8362617518593101,0.8348429263557018,0.8334162303199426,0.831983396721241,0.8305462139327758,0.8291065224580436,0.8276662113189082,0.8262272141031032,0.8247915046706806,0.8233610925208301,0.8219380178226678,0.8205243461159776,0.8191221626905492,0.8177335666556699,0.8163606647145227,0.815005564661718,0.8136703686259366,0.8123571660836728,0.8110680266743113,0.8098049928512063,0.8085700724080016,0.8073652309240467,0.8061923841773274,0.8050533905777348,0.8039500436775711,0.8028840648198002,0.8018570959875071,0.800870692920166,0.7999263185634262,0.7990253369190886,0.7981690073605597,0.7973584794762908,0.79659478849943,0.7958788513761632,0.7952114635180489,0.7945932962752004,0.7940248951576259,0.793506678821681,0.7930389388276959,0.7926218401637783,0.7922554225198781,0.791939602285812,0.7916741752373352,0.7914588198658593,0.7912931013001802,0.7911764757627968,0.7911082954991142,0.7910878141150588,0.7911141922573195,0.7911865035704766],[0.8467708743025475,0.8452903878808741,0.8437974183416572,0.8422938492151177,0.8407816349839149,0.8392627976930485,0.8377394231444498,0.8362136566692596,0.8346876984723063,0.8331637985450351,0.8316442511451069,0.830131388843145,0.828627576139705,0.8271352026585188,0.825656675925478,0.8241944137467345,0.8227508362037433,0.8213283572881106,0.8199293762047802,0.8185562683783756,0.8172113762044484,0.8158969995948684,0.8146153863745912,0.813368722595345,0.8121591228402568,0.8109886206017312,0.8098591588227476,0.8087725806986613,0.8077306208421902,0.8067348969179973,0.8057869018547071,0.8048879967408339,0.8040394045066176,0.8032422044859634,0.8024973279414703,0.8018055546211666,0.8011675103983479,0.8005836660265215,0.8000543370206376,0.7995796846544266,0.7991597180427459,0.7987942972582314,0.7984831374141075,0.7982258136303181,0.798021766788684,0.7978703099747418,0.7977706354992886,0.797721822391248,0.7977228442549578,0.7977725773889006],[0.8585780600860614,0.8570518051292103,0.8555078802310212,0.8539483042361581,0.8523751841710443,0.8507907118257766,0.8491971598472242,0.8475968773324076,0.8459922849123158,0.8443858693174687,0.8427801774178265,0.8411778097311208,0.8395814133954129,0.8379936746037608,0.8364173105013628,0.8348550605486265,0.8333096773573564,0.8317839170118646,0.8302805288924484,0.8288022450255071,0.8273517689928005,0.8259317644421256,0.8245448432531324,0.8231935534251702,0.8218803667689377,0.8206076665000333,0.8193777348499531,0.8181927408279412,0.8170547282845101,0.8159656044431501,0.8149271290793161,0.8139409045335877,0.8130083667472972,0.8121307775025097,0.8113092180329616,0.8105445841482224,0.8098375829803738,0.8091887314224663,0.8085983562832258,0.8080665961358559,0.8075934047935228,0.8071785563031889,0.8068216513153844,0.8065221246618883,0.8062792539568909,0.806092169029841,0.8059598619989634,0.8058811978020184,0.8058549250135775,0.8058796867943298],[0.8717282367574971,0.8701790648756282,0.8686065743466104,0.8670128963524733,0.8654002683987323,0.8637710308766556,0.8621276230671772,0.860472578575304,0.858808520184703,0.8571381541228437,0.8554642637276758,0.85378970250729,0.852117386584419,0.850450286518074,0.8487914184950897,0.8471438348850762,0.8455106141533231,0.8438948501278448,0.8422996406192077,0.84072807539542,0.839183223519374,0.8376681200636455,0.8361857522275172,0.8347390448945349,0.8333308456866223,0.8319639095934398,0.830640883284054,0.8293642892423713,0.828136509907999,0.8269597720490709,0.8258361316405006,0.824767459565981,0.8237554284986914,0.8228015013368305,0.8219069215679323,0.821072705904201,0.8202996394669585,0.8195882737041578,0.8189389271090101,0.8183516886830726,0.8178264239686418,0.8173627833765661,0.8169602124659353,0.8166179637950169,0.8163351099563425,0.8161105574271984,0.815943060902319,0.8158312378207042,0.8157735828469243,0.8157684821143554],[0.8861707348399669,0.8846281896775795,0.8830564167346919,0.8814576337710401,0.8798341832148555,0.8781885285612854,0.87652325013244,0.8748410401931316,0.8731446974178358,0.8714371207054721,0.8697213023392647,0.8680003204891733,0.8662773310541235,0.8645555588406237,0.8628382880732215,0.8611288522307864,0.8594306232007978,0.8577469997417677,0.8560813952418068,0.854437224759266,0.852817891329686,0.8512267715222456,0.8496672002291453,0.848142454673609,0.84665573762762,0.845210159840851,0.8438087216999526,0.8424542941660164,0.8411495990824177,0.8398971890116016,0.8386994268543917,0.8375584656344441,0.8364762289927866,0.835454393118971,0.8344943710109973,0.8335973000470911,0.8327640338000475,0.8319951387842586,0.8312908964146684,0.8306513099686019,0.8300761159069436,0.8295647986349477,0.8291166076975938,0.8287305764742967,0.8284055415955859,0.8281401624879742,0.827932940622596,0.8277822381809176,0.8276862959542503,0.8276432503675002],[0.9017292020224981,0.9002281295692414,0.8986919272314883,0.897122877144947,0.8955234044757483,0.8938960733433559,0.8922435819885465,0.8905687571915674,0.8888745479486716,0.8871640184176216,0.8854403401443356,0.8837067835836534,0.8819667089271096,0.8802235562496994,0.8784808349859029,0.8767421127427021,0.8750110034541108,0.8732911548778313,0.8715862354301694,0.8698999203503536,0.8682358771799586,0.8665977505373842,0.8649891461612451,0.8634136141903106,0.8618746316412749,0.8603755840393528,0.8589197461506788,0.8575102617602086,0.8561501224352214,0.8548421452147057,0.8535889491741222,0.8523929308458761,0.8512562385612479,0.8501807460021213,0.8491680257992155,0.8482193251897537,0.8473355475598194,0.8465172447525302,0.8457646228757028,0.8450775596518879,0.8444556285057994,0.843898125198127,0.8434040946516821,0.842972356938442,0.8426015320408629,0.8422900632685107,0.8420362393161365,0.8418382149897703,0.8416940306424084,0.8416016303656477],[0.9180770953781822,0.9166550007018852,0.9151921632039545,0.9136909145550192,0.912153748251687,0.9105833146096604,0.908982414822255,0.9073539941091004,0.9057011339856861,0.9040270436889271,0.9023350507968582,0.9006285910819155,0.8989111976370288,0.8971864893120081,0.8954581584945706,0.8937299582659276,0.892005688955418,0.8902891841122584,0.8885842959054442,0.886894879955212,0.8852247795915348,0.8835778095269388,0.881957738922681,0.8803682738190419,0.8788130388922892,0.8772955584927459,0.8758192369103989,0.8743873378065672,0.8730029627423611,0.8716690287268801,0.8703882447004543,0.8691630868607323,0.8679957727327966,0.8668882338822164,0.8658420871960997,0.8648586049364675,0.8639386862392497,0.8630828422756438,0.8622912084576702,0.8615635736428352,0.8608994120624103,0.8602979140594614,0.859758015217774,0.8592784238965709,0.8588576472293444,0.8584940156467825,0.8581857059798633,0.8579307631946789,0.8577271208063505,0.857572620015793],[0.9347266465552104,0.9334201163727531,0.9320677707488717,0.9306719826018124,0.9292353065033295,0.9277604721045157,0.9262503763528046,0.9247080745630146,0.9231367704161316,0.9215398049670582,0.9199206447467159,0.918282869044566,0.916630156455184,0.9149662707671009,0.9132950462643793,0.9116203725016057,0.9099461786018569,0.9082764171151786,0.9066150474627225,0.9049660189794011,0.9033332535561398,0.9017206278719283,0.9001319551962359,0.89857096673443,0.8970412924831513,0.895546441560096,0.8940897819748244,0.892674519816737,0.8913036778579224,0.8899800736101584,0.8887062969502557,0.8874846875566208,0.8863173126091167,0.8852059455178701,0.8841520468557014,0.8831567490807112,0.8822208468349276,0.8813447943247655,0.880528710435746,0.8797723910825762,0.8790753273529366,0.8784367276112734,0.8778555418559472,0.8773304870142897,0.8768600722802663,0.8764426239336931,0.8760763093082873,0.8757591597190293,0.8754890922448785,0.8752639303129458],[0.9510388630339908,0.9498798286865315,0.9486706751624281,0.9474138131051497,0.9461118562184561,0.9447676121538,0.9433840717706351,0.941964396915812,0.9405119068879253,0.9390300637636091,0.9375224567654988,0.9359927858464338,0.9344448446524654,0.9328825030099458,0.9313096890607623,0.9297303711465793,0.9281485395190947,0.9265681879304303,0.9249932951370669,0.9234278063332443,0.921875614516439,0.9203405417791616,0.9188263205186066,0.917336574559449,0.9158748001961863,0.9144443471808982,0.9130483997114938,0.9116899575156848,0.9103718171782705,0.9090965539242573,0.9078665041465168,0.9066837490499564,0.9055500998659444,0.9044670851575595,0.9034359407703045,0.9024576029655539,0.9015327051917515,0.9006615787994221,0.899844257805398,0.8990804875886188,0.8983697371911515,0.8977112147351267,0.8971038853674593,0.8965464911108708,0.896037572020468,0.8955754881020814,0.8951584415238912,0.8947844987325384,0.8944516121599495,0.8941576412730831],[0.9662593849705435,0.9652721196674877,0.9642314827670985,0.96313992674296,0.9620001307999,0.9608149875729052,0.9595875875511277,0.9583212015794617,0.9570192618235333,0.9556853415919414,0.9543231343944202,0.9529364325803544,0.9515291058539659,0.950105079906188,0.9486683153440034,0.9472227870404549,0.945772463976329,0.9443212896003025,0.9428731626998993,0.9414319187517365,0.9400013117067058,0.9385849961634375,0.9371865098912606,0.9358092566808245,0.9344564895255945,0.9331312941692671,0.9318365730912749,0.9305750300432303,0.9293491552912813,0.9281612117604364,0.9270132223139549,0.9259069584304765,0.9248439305601773,0.9238253804452634,0.922852275676857,0.9219253067281337,0.9210448866527207,0.920211153570143,0.9194239759809658,0.9186829608691283,0.9179874644645462,0.9173366054616544,0.9167292804244259,0.9161641810587965,0.9156398130007342,0.9151545157519911,0.9147064833941492,0.9142937857223847,0.9139143894608371,0.9135661792488717],[0.9795819338752171,0.9787813700065514,0.9779256776869397,0.977017371678066,0.9760592199957487,0.9750542230661189,0.9740055895816815,0.9729167099964215,0.9717911286205525,0.9706325152116888,0.9694446368336607,0.9682313305933479,0.9669964776931643,0.9657439790702301,0.9644777327447063,0.9632016128760628,0.9619194504301005,0.960635015291606,0.9593519996162047,0.9580740021976384,0.9568045136304264,0.9555469020689145,0.9543043994186738,0.9530800878413498,0.9518768865058117,0.9506975385737015,0.949544598463032,0.9484204194868089,0.9473271420122528,0.9462666823281344,0.9452407224411628,0.9442507010458839,0.9432978059250241,0.9423829680377338,0.9415068575415304,0.9406698819697659,0.93987218675087,0.9391136582094916,0.938393929134624,0.9377123869380812,0.9370681843607616,0.9364602526168755,0.9358873168006604,0.9353479133189936,0.9348404090594199,0.9343630219588889,0.933913842605766,0.933490856487837,0.9330919664926682,0.9327150152738147],[0.9902403828209791,0.9896318769043013,0.9889686786914204,0.9882534134008278,0.9874889873682002,0.9866785513594398,0.9858254594611539,0.9849332263933083,0.9840054856070168,0.9830459498901734,0.9820583755857373,0.9810465310103488,0.9800141692578963,0.9789650052697842,0.9779026968326692,0.9768308290104905,0.9757529014206845,0.9746723177174854,0.9735923766421687,0.972516264035113,0.9714470452705262,0.9703876576640692,0.9693409025082182,0.9683094365021248,0.9672957624547104,0.9663022192459991,0.9653309711276994,0.9643839965271778,0.9634630765878794,0.9625697837336783,0.9617054705852877,0.9608712595846546,0.960068033699117,0.9592964285817216,0.9585568265578376,0.9578493527906619,0.9571738739488949,0.9565299996577322,0.9559170869585762,0.9553342479330172,0.9547803605629552,0.9542540828028427,0.953753869734863,0.953277993568039,0.9528245661339068,0.9523915634313824,0.9519768516893993,0.9515782143544161,0.9511933793764842,0.9508200461652908],[0.9976330326180827,0.9972134456069592,0.9967427939246212,0.9962238901197426,0.9956598376602402,0.9950539588282473,0.9944097256526846,0.9937306974657261,0.9930204663960945,0.9922826113799568,0.9915206608992834,0.9907380643376719,0.9899381715178794,0.9891242196634187,0.9882993267373409,0.9874664898849147,0.9866285875674463,0.9857883839352801,0.9849485340499035,0.984111588717077,0.9832799979142363,0.9824561120592715,0.981642180645431,0.9808403480322418,0.9800526464146655,0.9792809861797082,0.9785271439974724,0.9777927490850616,0.9770792681347726,0.9763879894228755,0.9757200066225893,0.9750762028438661,0.9744572354204212,0.9738635219654621,0.9732952282233717,0.9727522582538823,0.9722342474935742,0.9717405592398011,0.9712702850845436,0.9708222497790223,0.9703950209229134,0.9699869237359645,0.9695960609812828,0.9692203378732911,0.9688574915337406,0.9685051242798287,0.9681607397702404,0.9678217808298208,0.9674856676502905,0.9671498350415088],[1.0014869470897054,1.001246954257477,1.0009638126179732,1.0006404476482738,1.0002800158181013,0.9998858195652975,0.9994612245290254,0.9990095841774969,0.9985341747887078,0.9980381429725249,0.9975244673231681,0.9969959349896464,0.9964551329327516,0.9959044525397739,0.9953461052793671,0.9947821463543092,0.9942145029310011,0.9936450035035047,0.993075405256856,0.9925074168756296,0.9919427150205616,0.9913829535584262,0.9908297654475842,0.9902847578362434,0.9897495013541717,0.9892255147674849,0.9887142461674756,0.988217051748071,0.9877351730581948,0.9872697134434808,0.9868216142450801,0.9863916312153711,0.9859803115462468,0.9855879718863477,0.9852146777498137,0.9848602247918243,0.9845241225457669,0.9842055813803969,0.9839035036307116,0.9836164800554448,0.9833427929264231,0.9830804270870765,0.9828270901452986,0.9825802425240595,0.9823371373717821,0.9820948694052916,0.9818504307693731,0.9816007711338269,0.9813428586819686,0.9810737384895514],[1.0020287093983098,1.0019554725134037,1.001850007018565,1.0017152419046425,1.0015542387452814,1.001370116640682,1.0011659686429775,1.000944774993773,1.000709319840368,1.0004621197474988,1.0002053733182588,0.9999409395482783,0.9996703472650079,0.999394831568853,0.9991153893062035,0.9988328452438264,0.9985479218898455,0.9982613068194836,0.9979737114002415,0.9976859149485044,0.9973987901441381,0.9971133092852027,0.9968305347829776,0.9965515990282917,0.996277678254014,0.9960099635672371,0.9957496309943301,0.9954978115029116,0.9952555614675698,0.9950238337851992,0.9948034497135534,0.994595071441238,0.994399175367448,0.9942160260609016,0.9940456508756911,0.9938878152306665,0.9937419986224826,0.9936073715708894,0.9934827739490613,0.9933666956421103,0.993257261368144,0.9931522229237815,0.993048963878015,0.9929445228235874,0.9928356400602001,0.992718828454816,0.992590464149073,0.9924468894117268,0.9922845187106311,0.992099938678806],[0.9999030808234651,0.9999842413243117,1.000044064866523,1.0000853290517429,1.0001108661181526,1.0001234929502005,1.000125933431746,1.0001207339880962,1.0001101729873882,1.0000961646480107,1.0000801622465836,1.000063119398147,1.0000455564572428,1.000027652952865,1.0000093383809316,0.9999903815281727,0.9999704789838633,0.9999493434291311,0.9999267922254638,0.9999028303613954,0.9998776809693405,0.9998517563713161,0.9998256205805139,0.9997999531408599,0.9997755142987039,0.9997531114307511,0.9997335666494218,0.999717685504975,0.9997062267026076,0.9996998727522063,0.9996992014680397,0.99970465823552,0.9997165289619655,0.9997349136280196,0.9997597003560508,0.9997905399113258,0.9998268205510695,0.9998676431356838,0.9999117964153743,0.9999577324042321,1.0000035417525293,1.0000469290264657,1.0000851878049808,1.0001151798186112,1.0001333665902525,1.0001359212718182,1.0001188591482768,1.0000781690635236,1.0000099459865166,0.9999105252058812]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],"xaxis":"x2","y":[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],"yaxis":"y2","z":[[0.08536583391667761,0.08526710377692905,0.08517947810586263,0.08510317121214736,0.08503837016432145,0.08498523366109083,0.08494389105026058,0.0849144415075575,0.08489695338507931,0.08489146373739924,0.08489797803149206,0.08491647004466255,0.08494688195258306,0.08498912460742226,0.08504307800391013,0.08510859192908049,0.0851854867893918,0.08527355460699644,0.08537256017513736,0.08548224236102787,0.08560231554315266,0.08573247116871688,0.08587237941600462,0.0860216909456766,0.08618003872455725,0.0863470399052256,0.08652229774472481,0.08670540354593448,0.08689593860558903,0.08709347615355069,0.08729758326874824,0.08750782275813314,0.0877237549860678,0.08794493964271984,0.08817093744126148,0.08840131173494936,0.08863563004644957,0.08887346550307279,0.08911439817285866,0.08935801629769043,0.0896039174208117,0.08985170940724484,0.09010101135666566,0.09035145440926337,0.09060268244600324,0.09085435268550786,0.09110613618048015,0.09135771821720767,0.09160879862221241,0.09185909198054963],[0.08149875398584801,0.08136969980121762,0.08125486153869137,0.08115454660207118,0.08106902441942566,0.08099852459997152,0.08094323532298699,0.08090330198011299,0.0808788260896544,0.08086986449834038,0.08087642888249746,0.08089848555680236,0.08093595559479684,0.08098871526124411,0.08105659675228631,0.08113938923531117,0.08123684017654512,0.08134865694074639,0.08147450864404822,0.0816140282380706,0.08176681480092461,0.08193243600872446,0.08211043075971677,0.0823003119221497,0.08250156917652808,0.08271367192292214,0.08293607222448404,0.08316820775924114,0.0834095047535336,0.08365938087208909,0.08391724804162826,0.08418251518701043,0.08445459086120405,0.08473288575274454,0.08501681505677036,0.08530580069816066,0.08559927339768919,0.08589667457442442,0.08619745807980986,0.08650109176093249,0.08680705885240297,0.08711485919802162,0.08742401030497593,0.08773404823470518,0.08804452833577456,0.08835502582512869,0.08866513622494625,0.08897447566300362,0.08928268104498498,0.08958941010755828],[0.07700869772947122,0.07683980293595996,0.07668905103987778,0.07655688917383863,0.07644371125820681,0.07634985489807611,0.0762755986480939,0.07622115968777497,0.07618669194486856,0.07617228469827103,0.07617796168504631,0.07620368072849455,0.07624933389609584,0.07631474818775842,0.07639968674636329,0.07650385057433842,0.07662688073214845,0.07676836098735171,0.07692782087644354,0.07710473913621531,0.0772985474569285,0.07750863450630434,0.07773435017118942,0.07797500996277218,0.078229899531344,0.07849827923775084,0.0787793887307583,0.07907245148243931,0.0793766792372459,0.07969127633451363,0.08001544386861498,0.08034838365569845,0.08068930198078915,0.08103741310386582,0.08139194250827184,0.08175212987936703,0.08211723180562452,0.08248652419835356,0.08285930442985921,0.08323489319309499,0.08361263608872439,0.0839919049479663,0.08437209890167788,0.08475264520783019,0.08513299985088324,0.08551264792759017,0.08589110383448194,0.08626791127273534,0.08664264308633302,0.08701490094942174],[0.07185910198164103,0.07163752492031043,0.07143902201495655,0.0712642555929308,0.07111381309501484,0.07098820164223986,0.07088784319253426,0.07081307037789814,0.07076412310321822,0.07074114597564068,0.07074418661891554,0.07077319491073687,0.07082802316335672,0.0709084272492385,0.07101406865488062,0.07114451742782048,0.0712992559648509,0.07147768357418567,0.07167912173118096,0.07190281993660037,0.07214796207854093,0.07241367319412187,0.07269902652485713,0.07300305076015727,0.07332473736640512,0.07366304790422697,0.07401692124357055,0.07438528059462818,0.07476704028210844,0.07516111220048098,0.07556641189824104,0.07598186424964497,0.07640640868248043,0.0768390039400334,0.07727863236432636,0.07772430369579966,0.07817505839181779,0.07862997047265957,0.07908814990899149,0.07954874456924887,0.08001094174890308,0.08047396930633394,0.08093709643202318,0.08139963407911459,0.08186093508412853,0.0823203940068486,0.08277744671819606,0.08323156976433889,0.08368227953442102,0.0841291312581963],[0.06603824740962798,0.0657463730441847,0.0654837117390759,0.06525126797755489,0.06504994082667745,0.06488051395142344,0.06474364656940604,0.06463986555431031,0.06456955887857775,0.06453297056053885,0.06453019724890913,0.06456118653942748,0.06462573707599262,0.06472350044376297,0.06485398481634222,0.06501656027542196,0.06521046568100751,0.06543481693530581,0.06568861645481797,0.06597076364406805,0.0662800661511348,0.0666152516797414,0.06697498013465583,0.06735785588581401,0.06776243995087415,0.06818726191466636,0.06863083142598918,0.0690916491361942,0.06956821696886147,0.07005904763460986,0.07056267332887028,0.0710776535726372,0.07160258217633073,0.07213609332465806,0.07267686679560292,0.07322363233937908,0.07377517325343237,0.07433032919751217,0.07488799829866814,0.07544713859997791,0.07600676890913956,0.07656596910399435,0.07712387995183212,0.07767970249818484,0.07823269707893113,0.07878218200709798,0.07932753198290164,0.07986817627244944,0.0804035966972412,0.08093332547324188],[0.059575683713118555,0.059188869950134095,0.05883877707132503,0.058526974610431104,0.058254885696510106,0.05802376760582276,0.05783469371509493,0.05768853737749067,0.05758595821676732,0.057527391283768554,0.057513039443722415,0.05754286926585865,0.05761661057364874,0.057733759690977,0.05789358629419642,0.05809514365993364,0.05833728199079631,0.058618664411757386,0.05893778516321018,0.05929298947483902,0.059682494587848973,0.060104411400250565,0.060556766237830705,0.0610375222981461,0.06154460037182672,0.062075898510022265,0.0626293103746526,0.06320274207545261,0.06379412736161272,0.06440144109388299,0.065022710973876,0.06565602755024035,0.06629955255620136,0.06695152565998634,0.06761026972946083,0.06827419472571715,0.06894180034828779,0.06961167755802583,0.07028250910341759,0.07095306917297026,0.07162222229110372,0.07228892156827123,0.07295220640837759,0.07361119976836124,0.07426510505639493,0.07491320274678812,0.0755548467815249,0.0761894608205781,0.07681653439578472,0.07743561901620222],[0.05256885309925692,0.052051921238091665,0.051580514909776935,0.0511571754590557,0.050784252476670656,0.05046386349362235,0.05019785508482173,0.04998776680448015,0.049834799397584964,0.049739788659245165,0.04970318614147989,0.04972504764071972,0.049805030055713274,0.04994239681125899,0.05013603163156086,0.0503844600536494,0.0506858777293329,0.051038184299818996,0.05143902145684455,0.05188581373311357,0.05237581058773159,0.0529061284553244,0.05347379159124984,0.05407577074809069,0.05470901893932997,0.05537050376636249,0.056057235990460856,0.056766294212137476,0.05749484567101452,0.05824016329798771,0.05899963923911736,0.05977079513020714,0.060551289436429824,0.06133892218708591,0.06213163743602528,0.06292752376747514,0.06372481314848624,0.06452187840581998,0.06531722957913262,0.0661095093754727,0.06689748792365387,0.06768005700180552,0.06845622388789804,0.06922510496154288,0.06998591916601477,0.07073798142220891,0.07148069607104317,0.07221355040750539,0.072936108357955,0.07364800434224694],[0.045229472615665296,0.04453163062800684,0.043888500838145765,0.04330434492895806,0.042783227962879436,0.04232893134140475,0.04194486272949526,0.04163396691406923,0.041398642205672735,0.041240667280206804,0.04116114318397718,0.04116045453961213,0.041238252822940705,0.04139346304884427,0.041624313495438096,0.04192838643435337,0.04230268643433955,0.042743721827498374,0.043247594453785496,0.04381009282489619,0.04442678429522764,0.045093102571209444,0.04580442779163526,0.0465561573427685,0.04734376643346462,0.04816285818335798,0.04900920354128149,0.04987877174880858,0.050767752310939884,0.05167256955847597,0.05258989091386186,0.05351662993241714,0.054449945108126,0.05538723532692013,0.05632613273495868,0.057264493674706145,0.05820038823390848,0.059132088855369136,0.060058058370278944,0.06097693774493995,0.06188753376942709,0.06278880686595102,0.0636798591531312,0.0645599228687195,0.06542834922625747,0.06628459775955571,0.06712822619173267,0.06795888085199164,0.06877628765262087,0.06958024363028933],[0.037969412797105515,0.037019512359189814,0.03613033011344991,0.03530906391914734,0.03456295487932195,0.033899115593457846,0.03332432456669251,0.03284479400884514,0.03246592384911189,0.03219206009552061,0.032026279345500466,0.03197022195008448,0.03202399316799596,0.03218614467062794,0.032453739143084956,0.03282249049078423,0.03328696353550095,0.033840811767138504,0.0344770303774211,0.035188204024398845,0.035966733399165084,0.03680503028379645,0.03769567619304339,0.0386315441028892,0.0396058858654386,0.04061238972227134,0.041645213090340666,0.04269899580966913,0.04376885859862469,0.0448503907901141,0.0459396306813722,0.047033041120347174,0.048127482325171084,0.04922018341000557,0.0503087136712849,0.051390954363226896,0.05246507144619709,0.05352948961101261,0.0545828677525947,0.055624075975462206,0.05665217415156982,0.05766639201010066,0.058666110713017944,0.05965084585493525,0.06062023181780931,0.06157400740768229,0.06251200270044648,0.06343412702518059,0.06434035801617709,0.06523073166780645],[0.031553033938240375,0.030269311497632692,0.029039133914373388,0.0278732850231789,0.02678365225021034,0.025783111473694206,0.02488527460617691,0.024104060478638775,0.023453065030985463,0.02294474186800764,0.022589458669601856,0.022394556626907546,0.02236358375037092,0.022495869676791423,0.022786546163854834,0.023227011311890058,0.023805729852667823,0.024509199587604783,0.025322912334351053,0.02623218275379566,0.02722278097507779,0.028281359680829073,0.02939570126212064,0.030554825747273272,0.03174900132527637,0.03296969307078501,0.03420947686336934,0.03546193727011464,0.03672156149428417,0.03798363659864992,0.03924415386714712,0.040499722015409176,0.04174748965477118,0.04298507667699226,0.044210513853653065,0.04542218979353857,0.046618804379894456,0.04779932785772827,0.048962964822738125,0.0501091224563262,0.05123738244334655,0.052347476094407444,0.05343926226989897,0.05451270776766244,0.055567869890690604,0.056604880956355456,0.05762393454553018,0.05862527331980398,0.059609178258915305,0.06057595918959877],[0.02725108791491774,0.02561520598433905,0.024000220565242442,0.022415464986833868,0.02087254836622886,0.01938600928242873,0.017974105922801076,0.016659675306173422,0.015470853577223845,0.014441196287355504,0.013608402278545477,0.013010674704002297,0.012680322651776217,0.01263598514642173,0.012876957563625814,0.013383026929475902,0.014119975729696404,0.015047483352310202,0.016125800290104346,0.01731961922891914,0.018599463035635387,0.019941577284002615,0.021327170607033596,0.022741499075509014,0.02417302062842795,0.025612693574505702,0.027053423595443944,0.028489638268086582,0.029916962791320414,0.031331972997128164,0.032732006280950215,0.03411501560173164,0.03547945547244785,0.036824191787520215,0.038148429522964565,0.03945165395384057,0.04073358220537045,0.04199412280481515,0.04323334151863318,0.0444514322081022,0.045648691763108026,0.0468254984117505,0.0479822928768478,0.04911956197671226,0.05023782435925201,0.05133761812472978,0.05241949014007617,0.05348398688155126,0.05453164666647115,0.05556299315148919],[0.02646331904526456,0.024660271087677873,0.022846577640754328,0.021024437585829458,0.019196404953089597,0.017365528949343106,0.015535590194674775,0.013711519834960974,0.011900187807908547,0.010111990999854013,0.008364323461347778,0.006689892569124406,0.005158468922591062,0.003933548144179389,0.003354751188555426,0.003718822800038419,0.004799836276823784,0.0062198933023482495,0.007781567866361497,0.009401544284194787,0.011042229397197765,0.01268463644574562,0.014318168334254783,0.01593643792321267,0.01753538548616495,0.019112353163718145,0.02066559339268983,0.022193989083829187,0.023696883730581014,0.025173971674037923,0.026625222811385386,0.028050827833232626,0.0294511561640129,0.030826722065948692,0.03217815621164501,0.03350618110126464,0.03481158933969586,0.03609522417917276,0.03735796197373857,0.03860069634079194,0.03982432391527513,0.04102973163424301,0.04221778551645899,0.04338932091177001,0.044545134194088995,0.04568597586399668,0.04681254501525941,0.04792548510619532,0.04902538096344824,0.05011275693353508],[0.02935647508028262,0.02766458205371574,0.025966336808410727,0.0242641719803456,0.022560876717149125,0.02085970450978592,0.01916453458788449,0.01748012003807066,0.01581248021998862,0.014169540186108253,0.012562204680676441,0.011006213633054809,0.009525409935202782,0.008157453793874192,0.0069630314555952,0.006036413279733471,0.005501320437810659,0.005458336312509536,0.0059019947180342525,0.006721282406323296,0.007784452289004182,0.008992758188665068,0.010283877810025311,0.011620248492707364,0.012979109671047862,0.014346377380806737,0.015713157760680645,0.017073769479001227,0.01842459515483559,0.019763391111730536,0.021088856440238442,0.02240035306608346,0.023697716486560678,0.024981122669507423,0.02625099087376055,0.02750791023966773,0.028752582704940542,0.02998577760282057,0.031208294998457033,0.03242093586288816,0.03362447782835972,0.03481965566510948,0.036007145860039114,0.03718755481945848,0.03836141029837611,0.039529155702056194,0.04069114692796858,0.04184765142856708,0.04299884918435074,0.044144835286518],[0.03457830196401563,0.03310130567334497,0.0316269236361579,0.030157932207452526,0.02869740535633911,0.027248763463469456,0.025815834267477994,0.024402929158258396,0.023014938620594574,0.02165745106916926,0.020336899210983226,0.01906073667076695,0.01783764350671574,0.01667774998521896,0.015592849831958147,0.014596542597018584,0.013704197331259306,0.012932574016155322,0.012298906493843496,0.01181930674498736,0.011506571584196457,0.01136785243768316,0.011402982360275541,0.011604203516407554,0.01195747999823648,0.012444866969522638,0.013047062201446392,0.013745444681619392,0.014523329867324419,0.015366515037164309,0.01626333373556871,0.017204437030630546,0.018182458936610833,0.019191659740310833,0.02022759442915604,0.021286825125971427,0.022366681406294563,0.02346506542210533,0.024580296176607962,0.025710986843513604,0.026855949475515162,0.028014122188322027,0.029184514664384462,0.030366168492540948,0.0315581294251318,0.03275942910387235,0.03396907419976717,0.03518604124858725,0.03640927575489715,0.0376376943923649],[0.04067843195348599,0.03938720430596551,0.03809797918124075,0.03681236039168974,0.035532003698046925,0.03425861455079758,0.03299394626583151,0.03173979908111583,0.03049802071127208,0.0292705092300771,0.02805921937022567,0.02686617363411877,0.025693479950979845,0.024543357975696335,0.023418176469761975,0.022320504478550187,0.02125317913179471,0.02021939270059318,0.019222800810021066,0.018267652056677366,0.017358936140312902,0.016502542178436715,0.015705410165486995,0.014975645807548966,0.014322552601985577,0.013756518332138581,0.013288684576473916,0.012930341973918482,0.012692047065023448,0.012582552496070857,0.012607753921979844,0.012769921862880028,0.01306744276337386,0.013495137546813907,0.014045036131888572,0.014707366380542854,0.015471513454730558,0.016326789076157228,0.01726295385815967,0.018270511990001393,0.019340833248978208,0.020466162285806274,0.02163956451402555,0.02285484309078651,0.024106448257105912,0.025389390617450124,0.02669916367503019,0.02803167728504092,0.029383201772060694,0.0307503215924851],[0.046793798551387336,0.045635898017927855,0.044474688312588634,0.043310684652118146,0.0421443531454428,0.04097610314746887,0.03980627997246631,0.03863515825646252,0.03746293631260682,0.03628973188130484,0.035115579737635814,0.03394043168236875,0.032764159511292176,0.031586561634332606,0.030407374108434453,0.029226286969159986,0.028042966916049336,0.02685708765777983,0.025668369603056646,0.024476631163577078,0.0232818548231873,0.022084272482901048,0.0208844766569662,0.01968356723687109,0.018483348305831173,0.017286596667574927,0.016097434399303216,0.01492185293523942,0.013768456036695683,0.01264950925116267,0.011582385924863213,0.010591429135782848,0.009709969775593928,0.008981516059815705,0.008457849516944083,0.00819091093442011,0.008218028190982395,0.008547688217078698,0.009157095922905107,0.010003405059224767,0.011038734322489682,0.012220040959449934,0.013512604851946896,0.014889783919357504,0.01633146736286628,0.01782243344727692,0.019351008312131723,0.020908072870939407,0.022486356730531957,0.02407994341258976],[0.052529996489157786,0.05146702206202804,0.05039507119690911,0.049314016946255805,0.04822366885643608,0.04712376917560216,0.04601398968065771,0.04489392926115931,0.04376311239998329,0.0426209886886954,0.04146693350926263,0.04030025000270031,0.039120172429355046,0.037925871004978295,0.036716458272108114,0.035490997038492775,0.03424850988469612,0.03298799021337217,0.03170841478512076,0.030408757662895705,0.029088005471731966,0.027745173876988456,0.02637932519772059,0.024989587110194163,0.023575172473064815,0.022135400443439614,0.020669719294798338,0.01917773177712455,0.01765922464695088,0.01611420550584241,0.014542953151011334,0.012946094284890262,0.011324735006022081,0.00968071569254594,0.008017174855934062,0.006340006005965061,0.004662477044007129,0.003025064100919402,0.0016310693052349853,0.0015715642639852164,0.002958358612745615,0.0046524427963031394,0.006422935251600678,0.008224900312507357,0.010043277276749881,0.011870764450630204,0.013702806874710462,0.015536051222520535,0.017367764121797868,0.019195580270820294],[0.05775347079241324,0.056764983614509774,0.05576338732376291,0.05474829036474891,0.05371925766495867,0.05267581121941114,0.051617431448178756,0.05054355941835938,0.049453600022983366,0.04834692621007521,0.04722288435614842,0.04608080088058819,0.04491999020180498,0.04373976414431505,0.04253944292018001,0.04131836783149758,0.04007591587695276,0.03881151650045553,0.03752467080154948,0.03621497364688089,0.03488213929598768,0.03352603140723859,0.03214669865729177,0.030744417745409314,0.02931974634820993,0.027873589775711954,0.026407286870086276,0.02492272342882676,0.02342248568227782,0.021910073018606244,0.020390199690172937,0.018869231948024683,0.01735583327485437,0.01586193002942505,0.014404163879711298,0.013006050046663711,0.011701033764748243,0.010536273904069388,0.009575659625376832,0.008897549982047543,0.008579789361140643,0.008670568100530822,0.009163797066469519,0.010003855063921138,0.011114145246380255,0.012422630610508998,0.013872343252929046,0.0154215914812221,0.017040646814618275,0.018708282536079403],[0.06245484651171963,0.06153378116709839,0.06059751271210447,0.0596456363132385,0.05867773358454844,0.057693376535483,0.05669213237939258,0.05567356928858645,0.05463726318857863,0.053582805692725444,0.052509813289613134,0.05141793791020639,0.0503068790211027,0.049176397415717416,0.04802633090870334,0.046856612182691465,0.04566728909338764,0.044458547812717505,0.043230739284414205,0.041984409587442074,0.04072033495612572,0.03943956239883707,0.03814345709696995,0.03683375805930863,0.03551264385716983,0.034182810668182254,0.03284756528944255,0.031510936188554425,0.030177805925730175,0.028854068172622982,0.027546811656353695,0.02626453095062442,0.0250173589553758,0.023817306424268915,0.022678477798691817,0.02161720784430189,0.020652030251434878,0.019803353750657594,0.01909270180949889,0.018541402582212194,0.01816873599456698,0.017989763941638245,0.018013315975128,0.018240717917842902,0.018665691917506225,0.01927545452940197,0.020052623348207167,0.020977352802579063,0.02202920886828125,0.023188529852972435],[0.06666913490069401,0.06581590132742939,0.06494721722716545,0.06406280169131975,0.06316238796816653,0.06224572929795374,0.061312605561190114,0.060362830807893,0.05939626174073223,0.0584128072311531,0.05741243895492404,0.05639520324233975,0.05536123424872066,0.05431076856302416,0.05324416138638968,0.052161904428161404,0.05106464568400739,0.049953211278390204,0.04882862957042071,0.04769215773567151,0.046545311043067535,0.04538989503972764,0.04422804082896914,0.043062243565003586,0.041895404174217804,0.04073087412241278,0.03957250274641141,0.03842468621356563,0.037292416510683914,0.036181327935085605,0.035097737308031375,0.0340486725202722,0.03304188207384209,0.0320858161386604,0.03118956761816186,0.030362760400721042,0.029615372257043512,0.028957482866340874,0.02839894433091983,0.027948982821844257,0.02761575493252229,0.027405898208876248,0.02732412758282269,0.027372932794092367,0.027552422720906324,0.02786034122760023,0.028292250824402992,0.02884185328261643,0.029501397991205516,0.030262123169064237],[0.0704327520396093,0.06965016454549486,0.06885322366788366,0.06804182125407031,0.06721588288077146,0.06637537409761614,0.06552030730420803,0.06465074929484724,0.06376682950469932,0.0628687489905167,0.06195679017779759,0.06103132740427198,0.06009283828651077,0.05914191593181035,0.05817928201069921,0.057205800695630644,0.0562224934575835,0.055230554693000374,0.0542313681269537,0.05322652390240723,0.05221783621717104,0.051207361306327706,0.05019741548471008,0.04919059285721667,0.048189782170018416,0.04719818210914949,0.04621931415200825,0.045257031842075725,0.0443155250925827,0.04339931784319249,0.042513257117984066,0.04166249130017908,0.04085243530325112,0.04008872035115581,0.03937712636876348,0.03872349561788373,0.038133627270714336,0.03761315412445303,0.037167404584301254,0.03680125522445572,0.036518981401536164,0.03632411516078512,0.036219320618617636,0.03620629676354361,0.03628571600986443,0.036457203956972196,0.03671936203843143,0.03706983069846083,0.03750538709013669,0.03802206862614332],[0.07376485510398889,0.07305463041800832,0.07233192890860496,0.07159680678632402,0.0708493641459182,0.07008975054744415,0.06931817099828981,0.06853489233827585,0.0677402500258284,0.06693465531816904,0.06611860283232365,0.0652926784662786,0.06445756765053957,0.06361406388934093,0.06276307753743361,0.061905644742306816,0.06104293646238738,0.06017626744868525,0.05930710504997311,0.058437077669391047,0.057567982662919175,0.05670179342721483,0.055840665375906366,0.05498694045008233,0.05414314975160648,0.05331201382913895,0.05249644008971115,0.05169951675824636,0.050924502770220516,0.050174812967299205,0.04945399798274596,0.04876571826457027,0.04811371180219143,0.04750175530821394,0.04693361886882702,0.04641301441632154,0.045943538787986744,0.045528612597848225,0.04517141662825765,0.04487482790085268,0.04464135795464168,0.04447309608363213,0.044371660314816264,0.04433815870429711,0.044373163087142634,0.04447669676067592,0.04464823676972055,0.04488673057964252,0.0451906260648141,0.04555791299820778],[0.07666376146321471,0.07602465334706272,0.07537524253434764,0.07471571356868446,0.07404629728858801,0.07336727523255063,0.07267898423786424,0.07198182121605835,0.07127624808282423,0.07056279681456475,0.06984207459716418,0.06911476902511848,0.0683816533007154,0.06764359137341594,0.06690154294888656,0.06615656828521371,0.06540983268067432,0.06466261054307496,0.06391628891521686,0.06317237031470632,0.06243247472945936,0.0616983405933771,0.06097182455052576,0.06025489980174754,0.05954965281624295,0.05885827818390349,0.05818307138396511,0.05752641925409635,0.05689078796375165,0.056278708328974796,0.0556927583551509,0.055135542961334,0.05460967092575305,0.05411772919669184,0.05366225483421643,0.05324570498218362,0.0528704254102691,0.05253861830375588,0.052252310103895985,0.05201332030191157,0.05182323215314038,0.05168336629375781,0.05159475820313046,0.051558140356734415,0.05157392975969179,0.05164222134716476,0.05176278749832158,0.051935083652738925,0.05215825976149162,0.05243117706924272],[0.07911110897528537,0.078538341984269,0.07795740444714688,0.0773685675154072,0.07677214612273069,0.07616850214936004,0.07555804763454155,0.07494124801321603,0.07431862534907314,0.07369076153164499,0.07305830140029813,0.07242195575279026,0.0717825041905072,0.07114079774662295,0.07049776123728763,0.06985439526963186,0.06921177783400369,0.06857106540159162,0.06793349344264975,0.06730037627520682,0.06667310614974532,0.06605315147229836,0.06544205406720614,0.06484142538195627,0.0642529415407071,0.06367833716091267,0.06311939785957406,0.0625779513926622,0.06205585739370567,0.06155499570576857,0.061077253335174164,0.06062451009512884,0.060198623052225314,0.05980140993752159,0.05943463173482916,0.059099974709792384,0.05879903219159813,0.05853328646165728,0.05830409113709217,0.05811265445816317,0.0579600238950642,0.05784707247867504,0.05777448723073437,0.05774276002156015,0.0577521811192968,0.05780283561647347,0.057894602831329134,0.05802715868772141,0.05819998098376825,0.05841235737097004],[0.08107857210807329,0.08056409035475554,0.08004332811372973,0.07951660818666434,0.07898429239168993,0.07844678366966537,0.07790452815312954,0.07735801717500589,0.07680778919143987,0.07625443159034925,0.07569858235438616,0.07514093154408005,0.07458222256400547,0.07402325317195556,0.07346487618838292,0.07290799986088439,0.07235358783637137,0.07180265869191688,0.07125628497425433,0.07071559169770394,0.07018175425110333,0.06965599566633945,0.06913958320452429,0.06863382422095668,0.06814006127696315,0.06765966647570154,0.06719403501017686,0.06674457792513218,0.06631271411013324,0.0658998615589359,0.06550742794986658,0.06513680062305548,0.06478933605238345,0.0644663489322166,0.06416910102054359,0.0638987898999977,0.06365653783537677,0.06344338091955841,0.06326025870810768,0.06310800454545383,0.06298733678157771,0.06289885106727015,0.06284301389813363,0.06282015755293915,0.06283047654144258,0.06287402564143138,0.06295071956605283,0.06306033426203317,0.06320250979903055,0.06337675477185677],[0.08253418741226382,0.08206728399947037,0.08159565371787732,0.08111964755786964,0.08063965047154383,0.08015608268389099,0.07966940092371719,0.07918009955511765,0.07868871158877015,0.07819580955078614,0.0777020061853905,0.07720795496632729,0.07671435039065849,0.07622192802758143,0.07573146429410682,0.07524377592897113,0.07475971913608663,0.07428018836923644,0.07380611473069035,0.07333846395803488,0.07287823397587495,0.07242645199225287,0.07198417112373001,0.07155246653814545,0.0711324311101534,0.07072517059176134,0.07033179830822922,0.06995342939878117,0.06959117463152108,0.06924613383255945,0.06891938898043287,0.06861199702813706,0.0683249825261647,0.06805933013043981,0.06781597708854872,0.06759580580572769,0.06739963659822898,0.06722822074553428,0.0670822339540363,0.06696227034299326,0.06686883705858666,0.06680234961374361,0.06676312804011317,0.06675139392446286,0.06676726838518586,0.06681077102610766,0.06688181988499085,0.06698023237376445,0.06710572718729672,0.06725792713821171],[0.08344712766313166,0.08301515925398605,0.0825796520114512,0.08214097310247988,0.0816995195442626,0.08125571897152253,0.08081003030372118,0.08036294429675345,0.07991498396291077,0.07946670484217426,0.0790186951072903,0.07857157548461409,0.07812599897241018,0.07768265033821688,0.07724224537704895,0.07680552991267643,0.07637327852502022,0.07594629298789388,0.07552540040293905,0.07511145101769318,0.07470531571832799,0.0743078831907366,0.07392005674734564,0.0735427508212896,0.07317688713440156,0.07282339055080965,0.0724831846337336,0.07215718692926397,0.07184630400737571,0.07155142629703579,0.07127342275885029,0.07101313544507251,0.07077137400274393,0.07054891018105089,0.07034647240841048,0.07016474050813563,0.07000434062355115,0.0698658404239718,0.06974974466185373,0.06965649114862002,0.06958644721209477,0.06953990669221431,0.06951708752381487,0.06951812994601621,0.06954309536726815,0.06959196590380795,0.06966464459742948,0.06976095630646334,0.0698806492520827,0.07002339719085064],[0.08379086882444178,0.08337990339129117,0.08296622274824407,0.08255020733662753,0.08213226498585266,0.08171283134624216,0.08129237021039915,0.08087137371014677,0.08045036237570947,0.08002988504355077,0.07961051859915652,0.07919286754107747,0.07877756335274867,0.07836526366901185,0.07795665122491113,0.07755243257523728,0.07715333657449391,0.07676011260847256,0.07637352857047905,0.07599436857746818,0.07562343042393024,0.0752615227743376,0.07490946209829397,0.0745680693562205,0.07423816644742395,0.07392057243668461,0.07361609958000485,0.07332554917479808,0.07304970726447346,0.07278934023197119,0.07254519032119729,0.07231797112936066,0.07210836311677939,0.07191700918365282,0.07174451036544842,0.07159142169979581,0.07145824831800292,0.07134544181342349,0.0712533969368587,0.07118244866594757,0.07113286969112145,0.07110486835522994,0.07109858707750479,0.07111410128526399,0.07115141886885833,0.07121048016704072,0.07129115848143093,0.071393261110293,0.07151653088368119,0.0716606481743702],[0.08354519947190302,0.08314055529828486,0.082733661355828,0.08232491439283195,0.08191473814716023,0.08150358362049456,0.0810919292289774,0.08068028081782941,0.08026917152738659,0.07985916149798666,0.0794508374012643,0.07904481178571493,0.0786417222248786,0.07824223025720499,0.07784702010760987,0.07745679718194852,0.0770722863271287,0.07669422985139017,0.07632338530139611,0.07596052299522758,0.07560642331314348,0.07526187375105922,0.07492766574508447,0.07460459127912192,0.07429343929141041,0.07399499189994765,0.0737100204708743,0.07343928155805375,0.07318351274614608,0.07294342843333075,0.07271971559336869,0.07251302955977876,0.07232398987741236,0.07215317626852262,0.07200112476142816,0.0718683240299709,0.0717552119910939,0.0716621727059682,0.07158953362716984,0.07153756323046843,0.07150646906489934,0.07149639624904545,0.07150742643498649,0.07153957725434038,0.07159280225340796,0.07166699131684194,0.07176197157169892,0.07187750875640889,0.07201330903230777,0.07216902120909909],[0.08269762811711984,0.08228433372206113,0.08186889211510529,0.08145172184799902,0.08103327042144641,0.08061401457225942,0.08019446041939857,0.07977514345470336,0.0793566283639946,0.07893950866426813,0.0785244061429199,0.07811197008536926,0.07770287627811387,0.07729782577518055,0.07689754341716254,0.07650277609358039,0.076114290741195,0.07573287207315743,0.07535932003651363,0.07499444699859706,0.0746390746662398,0.07429403074548635,0.0739601453535862,0.0736382471994153,0.07332915955307637,0.07303369603017279,0.07275265622103967,0.07248682119994176,0.07223694895377258,0.07200376977398032,0.07178798165915126,0.07159024577874737,0.07141118205078212,0.07125136488758127,0.07111131916410449,0.07099151646250156,0.07089237164458476,0.07081423980069845,0.0707574136190732,0.07072212121423745,0.07070852444652875,0.07071671775735808,0.07074672753681628,0.07079851203170034,0.07087196179330833,0.07096690065566262,0.07108308722641453,0.07122021686479647,0.07137792411383195,0.07155578554776704],[0.0812446293419928,0.08080787655284244,0.08036869254396752,0.07992752179019362,0.0794848422819673,0.07904116603416583,0.07859703943109703,0.07815304338876397,0.07770979331508658,0.07726793884858647,0.07682816335608907,0.07639118317032137,0.07595774654893026,0.07552863233745966,0.07510464832025378,0.07468662924514238,0.07427543451015561,0.07387194550344611,0.07347706259109513,0.07309170175156034,0.07271679086019063,0.07235326563246684,0.07200206524039046,0.07166412762266673,0.07134038451592274,0.07103175624104387,0.07073914628564676,0.07046343573055631,0.07020547757471053,0.06996609101895225,0.06974605577444251,0.06954610646570437,0.06936692720134256,0.06920914638707208,0.06907333185564554,0.06895998638646639,0.06886954368403495,0.06880236487889659,0.06875873560750903,0.06873886371857,0.0687428776430607,0.06877082545385303,0.06882267462853774,0.06889831251653325,0.06899754749893496,0.0691201108173534,0.0692656590365552,0.06943377709539926,0.06962398189164165,0.06983572633888695],[0.07919294646842893,0.07871863303135844,0.07824117475545699,0.07776104017706237,0.07727873868098836,0.0767948215272496,0.07630988269300404,0.07582455950248865,0.07533953301653054,0.07485552815223757,0.07437331350276796,0.07389370082672528,0.07341754417679791,0.07294573863785081,0.07247921864587617,0.07201895586111061,0.07156595657133343,0.0711212586049589,0.07068592773811593,0.07026105358553497,0.06984774497178305,0.06944712478721499,0.06906032434192139,0.06868847724087493,0.06833271281427711,0.06799414914860157,0.06767388577575281,0.06737299608979314,0.06709251957244697,0.06683345391963334,0.06659674717112382,0.06638328995358218,0.0661939079532222,0.06602935473766908,0.06589030504694565,0.06577734867053961,0.0656909850210847,0.06563161850530427,0.06559955477967076,0.065594997962062,0.06561804885202649,0.06566870419172861,0.06574685697796802,0.06585229781364832,0.06598471726553076,0.06614370917484125,0.06632877484901735,0.06653932804719634,0.06677470065940982,0.06703414897016784],[0.0765608877242642,0.07603635690827427,0.07550748477301732,0.07497475029454749,0.07443868325826608,0.07389986623676802,0.07335893638201033,0.07281658699284684,0.07227356881599191,0.07173069103560174,0.07118882190398645,0.07064888896360876,0.07011187880860803,0.0695788363327896,0.06905086341050734,0.0685291169573581,0.06801480631932677,0.06750918994220735,0.06701357127803152,0.06652929389209955,0.06605773574325124,0.0656003026214142,0.06515842074033665,0.06473352849978427,0.06432706745025422,0.06394047251421071,0.06357516154057263,0.0632325242931082,0.0629139109977489,0.06262062059768568,0.062353888887358766,0.062114876715901914,0.061904658466004375,0.06172421102431025,0.0615744034633019,0.061455987651271006,0.06136958999593735,0.06131570450840105,0.061294687347732836,0.061306752973402635,0.06135197199414434,0.06143027075936891,0.06154143269473453,0.06168510133900394,0.06186078499687295,0.06206786288393583,0.062305592606952134,0.06257311879632937,0.06286948268901107,0.06319363244907315],[0.07337923297849518,0.07279431206172961,0.07220333030572551,0.07160674481742385,0.07100507524796708,0.07039890731193073,0.06978889617548643,0.06917576966237421,0.06856033122045348,0.06794346258515586,0.06732612606946381,0.06670936640320882,0.06609431203768902,0.06548217582508499,0.06487425497619896,0.06427193019503732,0.06367666388515945,0.06308999732108238,0.06251354667898266,0.06194899782519791,0.06139809976933441,0.060862656701926435,0.06034451855527466,0.059845570050956094,0.05936771822896068,0.058912878491611406,0.05848295924010139,0.058079845231862645,0.05770537984171652,0.05736134646685508,0.05704944937252544,0.05677129432864621,0.05652836943385789,0.056322026558904205,0.056153463862115956,0.05602370983296454,0.05593360930291897,0.055883811825139545,0.055874762766336315,0.05590669737746629,0.055979638018439276,0.05609339461056962,0.05624756828495253,0.05644155809145248,0.05667457053758536,0.05694563164450043,0.05725360114261862,0.05759718838483423,0.05797496953152563,0.05838540555837612],[0.06969103212602598,0.06903943439531053,0.06837955022141641,0.06771175702893381,0.06703650610113399,0.06635432831414623,0.06566583990180035,0.06497174819660702,0.06427285728244049,0.06357007348322607,0.06286441059922142,0.062156994788266605,0.06144906897366687,0.06074199664326447,0.0600372648859789,0.05933648649303387,0.05864140093186079,0.057953873982141954,0.057275895806832774,0.05660957721784186,0.055957143888305215,0.055320928263423504,0.05470335893232745,0.054106947247345966,0.05353427101734819,0.052987955161258544,0.05247064928849402,0.051985002275930996,0.051533634035357455,0.05111910480831236,0.05074388248118344,0.050410308573993146,0.05012056371028427,0.04987663350956294,0.04968027594348581,0.049532991248476016,0.04943599547921968,0.04939019871235398,0.04939618876638799,0.04945422109824038,0.04956421528137309,0.04972575818391686,0.049938113669761475,0.05020023836478679,0.050510802785865276,0.050868216939185175,0.05127065936776899,0.05171610856973009,0.05220237571593918,0.05272713765991175],[0.06554930140572728,0.06483036007923251,0.06410054511002494,0.06336006783586834,0.06260922022398814,0.06184838331433661,0.06107803600430344,0.060298764142242486,0.059511269886418666,0.05871638127257158,0.057915061916689665,0.05710842075913121,0.05629772173124081,0.05548439319535683,0.05467003697289925,0.0538564367324675,0.05304556546019752,0.05223959167801962,0.05144088401254923,0.05065201364960853,0.04987575413955342,0.049115077950988746,0.04837314911144632,0.047653311231830135,0.046959070198077296,0.04629407084198338,0.04566206698859995,0.045066884435307736,0.04451237666082055,0.04400237339894692,0.04354062264077035,0.04313072713575331,0.042776077016528705,0.04247978072581603,0.0422445969136928,0.042072870327346926,0.041966474863329675,0.04192676683973947,0.04195455114742849,0.042050062269344324,0.042212961271908864,0.042442348864458135,0.0427367936062563,0.043094373430917474,0.04351272795169029,0.04398911856990057,0.04452049325284169,0.04510355295640216,0.04573481699071775,0.046410685095737626],[0.06101160601329159,0.06023212240366111,0.05943918119561095,0.058632719998838186,0.0578127534127163,0.05697938401133981,0.05613281409100501,0.05527335820663035,0.054401456521860785,0.053517688993731945,0.05262279040576434,0.05171766625189213,0.05080340945595078,0.04988131788530269,0.04895291257972546,0.04801995656438719,0.047084474044314074,0.0461487696822315,0.045215447536443,0.04428742907475333,0.04336796947906332,0.04246067120969422,0.041569493508897166,0.04069875619609538,0.03985313576013413,0.03903765141797699,0.038257638536282154,0.037518706676661386,0.03682667962508631,0.036187515215582805,0.035607203672650946,0.035091644660317174,0.0346465052505947,0.034277063503152676,0.03398804501810327,0.033783462263449054,0.03366646816022817,0.03363923581323848,0.03370287505146699,0.03385739355322321,0.034101706128807675,0.034433690910401764,0.03485028661477558,0.03534762149176526,0.03592116256588155,0.036565873453002634,0.03727637016351044,0.03804706642695528,0.038872302655807385,0.03974645523327386],[0.056131117090142,0.05530682714580616,0.05446717222618863,0.05361171295336814,0.0527400674344976,0.05185192354575368,0.05094705231064334,0.0500253224678974,0.04908671634292508,0.04813134715863574,0.04715947794632099,0.04617154224492894,0.04516816680671321,0.04415019655749154,0.04311872208812765,0.04207510997627361,0.04102103624743946,0.03995852327215586,0.03888998034644728,0.037818248094236444,0.03674664663146767,0.03567902709954797,0.03461982565270943,0.03357411819767608,0.03254767305060092,0.031546997112058,0.030579369109760283,0.029652850942460736,0.028776265358942395,0.027959125577220845,0.027211500837047698,0.02654380258092179,0.02596648059928813,0.025489628538365,0.025122514101706808,0.024873069348577942,0.02474739603916233,0.024749352986807235,0.024880290021650948,0.025138973562983655,0.025521715742109305,0.02602268234215611,0.026634326038914444,0.02734787830983767,0.028153836948345796,0.029042401552973558,0.030003829436503805,0.031028702927276115,0.03210811256979608,0.03323376852017991],[0.05094538863178343,0.050101273483611874,0.049241568752654605,0.048365404205157975,0.04747193116629576,0.04656033424254386,0.045629844114317565,0.04467975148586766,0.04370942230974289,0.042718314442825575,0.04170599594238313,0.04067216527672065,0.03961667380974574,0.03853955102699245,0.03744103310875215,0.0363215956318962,0.035181991405659446,0.03402329472988729,0.03284695372034154,0.03165485278777541,0.030449387894961166,0.02923355784591963,0.02801107555311881,0.026786503890384946,0.025565421163307407,0.024354620988048414,0.02316234965182266,0.02199857939000578,0.020875306082333508,0.019806841172756565,0.018810036093276992,0.017904330874180044,0.01711146270839776,0.016454629629507698,0.015956932425038782,0.015639084431798882,0.015516708160446013,0.015597909669797466,0.015881959994916765,0.016359595741340608,0.017014799950557914,0.01782737193619825,0.018775475670887713,0.019837623624923237,0.02099392644731462,0.022226700204047475,0.0235206237594001,0.02486263229079175,0.026241684025417367,0.027648485824314565],[0.04546691937427197,0.044635549414167794,0.04379128033798477,0.04293285362490807,0.042058987788106496,0.041168389043026755,0.04025976276900956,0.03933182572017315,0.0383833189505455,0.03741302143407553,0.03641976438396147,0.03540244630983397,0.03436004889882391,0.03329165387191178,0.03219646105695039,0.031073808044544737,0.02992319196806623,0.02874429419850486,0.02753700910617087,0.02630147857420194,0.025038134749777768,0.023747754746279246,0.0224315329281049,0.02109117947074798,0.019729058875169347,0.01834839041011631,0.01695354653225372,0.01555050963786787,0.0141475899139232,0.012756580756530002,0.01139465125378593,0.010087453468602852,0.008874056011946825,0.00781383692738152,0.006992441807488926,0.00651534555858491,0.006471128309074864,0.006876692167597254,0.007666203040718084,0.008738734138832928,0.010004161950123259,0.011397420816737358,0.01287501367231871,0.014408196747192766,0.015977627712630074,0.017569893082396357,0.019175375164642416,0.02078695040823453,0.022399184600570107,0.024007824556272053],[0.0396825559144655,0.03890016716221704,0.03811170896676209,0.037315685878679526,0.036510537293165175,0.03569465013546656,0.03486637261837281,0.03402402890674376,0.03316593451591471,0.03229041226969964,0.03139580865001114,0.03048051038399678,0.02954296113639434,0.02858167820510586,0.027595269158032173,0.026582448401378328,0.025542053738205357,0.02447306306857102,0.02337461151213465,0.022246009423197374,0.021086762056074078,0.01989659209568519,0.018675467022840713,0.017423634579414354,0.016141671914746802,0.01483055831673874,0.013491789890964338,0.012127572032725761,0.0107411639999586,0.009337540966766185,0.007924774014320405,0.006517199384041035,0.005143584214923446,0.00387087438127746,0.0028753295968703663,0.0025482260404361963,0.003133034058664941,0.004284287641553085,0.005674205530794758,0.007168842517216133,0.00871563984825523,0.01029063959048767,0.01188106929998405,0.013479152111840925,0.015079622047860496,0.01667861152050581,0.018273105747832544,0.019860654036406276,0.021439206680289508,0.02300701729254072],[0.03356953433634167,0.03287060108906918,0.032177580767431435,0.03148894821763275,0.03080306742216988,0.030118211824859176,0.02943258745471278,0.028744358619859772,0.0280516759426637,0.02735270653841556,0.02664566620651142,0.025928853609159502,0.02520068656369183,0.0244597407779101,0.023704791624689185,0.022934859898927722,0.022149262951342993,0.021347673184683766,0.020530186677356708,0.01969740573168393,0.018850540508418955,0.017991536689960994,0.017123238368154495,0.016249598020437284,0.015375948144921853,0.014509350733675819,0.013659038476593829,0.01283694931664795,0.012058321957579346,0.011342245079662581,0.010711916388251757,0.01019417467044498,0.009817720141526654,0.009609606676002379,0.009590392875822428,0.00976959822416357,0.01014370247060327,0.010697772507368076,0.011409662404751929,0.012254617814474332,0.013208694540969597,0.01425059281294837,0.015362263991759089,0.01652881402770361,0.017738103469141602,0.018980273482581456,0.020247304091488772,0.021532641569940093,0.02283089914290311,0.024137622293101228],[0.027132123314234508,0.026544221638631363,0.025980292887439183,0.02543892780158096,0.024918497418066347,0.024417184380572717,0.023933021229222366,0.02346393485178285,0.023007796097925998,0.022562473467188034,0.02212588978373571,0.021696080860251536,0.021271255312397493,0.020849854890441756,0.0204306149159046,0.020012624615282727,0.01959538729293401,0.019178880339779377,0.018763614985403687,0.01835069541046351,0.017941876274528902,0.017539616801759778,0.017147128223646682,0.016768409550456893,0.0164082643538013,0.016072288674401667,0.01576681777809929,0.015498818113521969,0.015275711743699565,0.015105125238495633,0.01499456471899747,0.0149510333706016,0.014980624933600592,0.015088141470543824,0.015276789765933878,0.015548003273612283,0.015901415609539518,0.016334983089006185,0.016845227099461,0.017427550401923605,0.018076578098319064,0.01878648187635886,0.019551259984149166,0.020364959829645493,0.0212218416393828,0.02211648897905562,0.023043875472844352,0.023999397825366076,0.024978884392976096,0.025978586967623833],[0.020455291838503968,0.01999628471226471,0.019587040142308377,0.01922613959557072,0.018911565389817846,0.01864075029622657,0.018410653174310534,0.01821785610051819,0.018058676673824204,0.017929288283396527,0.01782584116382031,0.017744577910247354,0.01768193851498566,0.01763465160737401,0.017599810148670812,0.01757493115077213,0.017557999944517306,0.017547500097443203,0.01754243031059067,0.017542309581886874,0.01754717169595395,0.01755754977223635,0.01757445125402345,0.017599323420179083,0.01763400931092186,0.01768069393156384,0.01774184077428796,0.0178201190998977,0.01791832304289536,0.01803928440047761,0.018185781851132357,0.018360450191750536,0.018565693826918146,0.018803609034654355,0.019075919351776258,0.01938392772536083,0.019728487916137724,0.02010999616031647,0.02052840250879988,0.020983239795106343,0.021473667030409153,0.021998523308109353,0.022556388054761553,0.023145643641713076,0.023764536869967726,0.02441123653356093,0.02508388503330872,0.025780642756268988,0.026499724591810308,0.02723942848917756],[0.013765585809825683,0.01344488944039635,0.013212354699327258,0.013065408760414185,0.012999445291148385,0.013008085189668837,0.013083594775669697,0.013217388342034007,0.01340053575673615,0.013624211040114114,0.013880044341358025,0.014160366271069265,0.01445835297275446,0.014768090680755354,0.015084581373589962,0.015403709311278917,0.01572218430906424,0.016037473272555412,0.016347727700941523,0.016651711877689063,0.01694873431359391,0.017238583548695032,0.01752146848986282,0.017797962910229042,0.018068953450220197,0.018335590357637727,0.018599240232872787,0.018861440170900877,0.019123852890043137,0.01938822268872228,0.019656332354567905,0.019929961441081934,0.020210846597823427,0.020500644860683998,0.020800900950493115,0.021113019667281106,0.02143824439002857,0.021777642496336007,0.022132098216407305,0.022502313057710895,0.02288881351775404,0.023291965384947114,0.0237119935533775,0.02414900598207518,0.024603020238296164,0.02507399098996623,0.025561836854321906,0.026066465156226917,0.026587793380515465,0.02712576639268155],[0.007492766471784536,0.007321451002632227,0.007307281151574894,0.007438245292784844,0.007694308290012943,0.008051471110218925,0.008485649299145203,0.00897520088246955,0.009502006652381205,0.010051561890124544,0.010612578579445,0.011176432114447923,0.011736622111013619,0.01228831237212738,0.012827962408741058,0.013353041355564463,0.013861808939561333,0.014353148476681515,0.01482643937240911,0.01528145941812901,0.01571830961367549,0.01613735612586872,0.016539185339530367,0.016924568870369694,0.01729443600403098,0.017649851412663384,0.017991996274365648,0.018322151157447546,0.018641679285287864,0.018952009101806385,0.019254615424881223,0.01955099889894145,0.019842663915715035,0.020131095628015898,0.020417737091619162,0.02070396788801225,0.02099108576310017,0.02128029283107626,0.021572687722275507,0.021869264703373196,0.022170920294792052,0.022478467301552077,0.02279265552350921,0.02311419779023117,0.023443799443730574,0.023782189026836462,0.024130147765163715,0.024488535472289852,0.024858310752949964,0.0252405437986561],[0.0024214612907267523,0.002483821388639383,0.002873897035622493,0.003456910179150855,0.004130941670909484,0.004840769092580141,0.005558360769707516,0.006269155664396745,0.006965303915668882,0.0076424663459766975,0.008298244003329278,0.00893136681493146,0.009541252948112679,0.010127758270078188,0.010691027101883873,0.011231398278996618,0.011749341927361701,0.01224541388089382,0.012720221248535507,0.013174396460719927,0.013608579192443572,0.014023406410411752,0.014419510789926452,0.014797527202480568,0.015158106166424502,0.015501932321458883,0.015829745319128907,0.016142360137459493,0.016440683787022084,0.016725725683605922,0.016998599586065862,0.017260515877332027,0.01751276402524062,0.017756686207672397,0.017993644221742187,0.018224982807176444,0.01845199328162624,0.018675881796793498,0.018897746485251665,0.01911856722486797,0.01933921070525646,0.019560452014435466,0.01978301222074309,0.02000760960858928,0.020235020567272676,0.02046614484886269,0.02070206917298206,0.020944123053042316,0.021193921249161345,0.021453388332592808],[0.0018155107424616148,0.002015811638348247,0.002423910210160054,0.0029275082076158005,0.003465146695527577,0.004008164854030882,0.0045434786237909695,0.005065186686956446,0.005570786948928228,0.006059413118189493,0.006530980874637896,0.006985773655904351,0.007424252365600375,0.00784697730609004,0.008254577941580337,0.008647732343150728,0.00902713634013118,0.009393456458316702,0.009747271167196259,0.010089011325457926,0.010418912763046639,0.010736992134722817,0.011043052710373175,0.011336721199784487,0.011617511513642384,0.0118849075294427,0.012138454845492658,0.01237785105570623,0.012603024877258345,0.012814196071485475,0.01301191015850137,0.013197044218750145,0.013370782506810727,0.013534563156647717,0.013689999924884995,0.013838785635020882,0.013982586578533076,0.014122939296538097,0.014261162493661873,0.014398296865048388,0.014535083956908208,0.014671991651623275,0.014809288639909575,0.014947163912038238,0.015085880848143118,0.01522595007884624,0.015368301954327116,0.015514438795624247,0.015666549104995514,0.015827570049013424],[0.002432046900562667,0.0024553393650204236,0.0025735763767537716,0.002747709544701848,0.002948761544434647,0.0031590613637869818,0.0033694705051623038,0.0035761849883887272,0.0037782450736223924,0.0039758695760645614,0.00416950525840586,0.0043594481913051975,0.004545865146260247,0.004729017868902529,0.004909504239478403,0.005088381024410358,0.005267102446432403,0.005447278277616759,0.005630314139744455,0.005817034823084714,0.006007395590718593,0.006200352722406964,0.006393910223434437,0.006585312598369542,0.00677133011671075,0.00694858154372089,0.007113850244613591,0.007264364038857474,0.0073980218794402934,0.007513559225529994,0.007610648790120739,0.007689935153700571,0.007753001908881763,0.0078022699752836235,0.007840826879657365,0.007872190359347699,0.007900016461778183,0.007927772435378486,0.007958406947763537,0.007994061872897225,0.008035877293909468,0.008083940443341904,0.008137416590089552,0.008194873371983592,0.008254771937260446,0.008316058945319003,0.008378768750044513,0.008444543056343567,0.008516990180847646,0.008601827817808716],[0.0014909964715004822,0.0012235431318124899,0.0010785081494873506,0.001031545720006018,0.0010399702521909533,0.0010663653607354082,0.0010899438209617468,0.0011038579102467677,0.001109137030785944,0.001109512760451884,0.0011076281618372878,0.0011034501008389797,0.0010954432016280816,0.001082983445286344,0.0010688852896771099,0.0010613054149462898,0.0010739198258388264,0.001122732369160801,0.0012193684766869798,0.001365133768317063,0.0015513754935356475,0.0017645409759305506,0.0019904318209088487,0.002216142213818275,0.0024305732457080916,0.002624419039618928,0.0027900397142832274,0.0029213516473549127,0.0030137583177370975,0.0030641153718217436,0.0030707195877332063,0.003033314120144111,0.002953106111287355,0.002832796147152865,0.0026766219286039825,0.0024904204376617915,0.002281711560477107,0.0020597941630364556,0.0018358024818051287,0.0016225498143831775,0.0014337230294956477,0.0012816581763569277,0.0011732155172895374,0.0011054863298240155,0.0010663203928655493,0.0010417635798702107,0.001025704873431318,0.001027833030587243,0.001077033432907521,0.0012128898289640005]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.328092\u003cbr\u003egamma: 1000","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 10\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1.69308e-09\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 3.85096e-06\u003cbr\u003egamma: 1000","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 6.25486e-08\u003cbr\u003egamma: 1000","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1e-09\u003cbr\u003egamma: 344.751"],"visible":true,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],"xaxis":"x","y":[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.72 (SEM: None)\u003cbr\u003eC: 1.05541e-06\u003cbr\u003egamma: 0.000121461","Arm 1_0\u003cbr\u003eaccuracy: 0.86 (SEM: None)\u003cbr\u003eC: 0.0145292\u003cbr\u003egamma: 19.803","Arm 2_0\u003cbr\u003eaccuracy: 0.723333 (SEM: None)\u003cbr\u003eC: 0.0781103\u003cbr\u003egamma: 0.000891485","Arm 3_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 0.328092\u003cbr\u003egamma: 1000","Arm 4_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 10\u003cbr\u003egamma: 1000","Arm 5_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1.69308e-09\u003cbr\u003egamma: 1000","Arm 6_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 3.85096e-06\u003cbr\u003egamma: 1000","Arm 7_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 6.25486e-08\u003cbr\u003egamma: 1000","Arm 8_0\u003cbr\u003eaccuracy: 1 (SEM: None)\u003cbr\u003eC: 1e-09\u003cbr\u003egamma: 344.751"],"visible":true,"x":[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],"xaxis":"x2","y":[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],"yaxis":"y2","type":"scatter"}],                        {"annotations":[{"font":{"size":14},"showarrow":false,"text":"Mean","x":0.25,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"font":{"size":14},"showarrow":false,"text":"Standard Error","x":0.8,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"showarrow":false,"text":"x-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.26,"yanchor":"top","yref":"paper"},{"showarrow":false,"text":"y-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.4,"yanchor":"top","yref":"paper"}],"autosize":true,"height":450,"hovermode":"closest","legend":{"orientation":"v","x":0,"y":-0.2,"yanchor":"top"},"margin":{"b":100,"l":35,"pad":0,"r":35,"t":35},"title":{"text":"accuracy"},"updatemenus":[{"buttons":[{"args":[{"x":[[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09]],"y":[[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736]],"z":[[[1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272,1.0021656893709272],[1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361,1.0020563594454361],[1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279,1.001912273631279],[1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116,1.001736364417116],[1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185,1.001531716920185],[1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903,1.0013014927533903],[1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073,1.0010488468370073],[1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375,1.0007768433099375],[1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043,1.0004883772293043],[1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154,1.0001861091032154],[0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698,0.9998724189469698],[0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619,0.9995493846813619],[0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228,0.9992187861958228],[0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051,0.9988821324268051],[0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845,0.9985407059367845],[0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144,0.9981956183747144],[0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483,0.9978478703126483],[0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799,0.9974984094262799],[0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551,0.997148181480551],[0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027,0.9967981694243027],[0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524,0.9964494175913524],[0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195,0.9961030404833195],[0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622,0.9957602180222622],[0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693,0.9954221805670693],[0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657,0.9950901871472657],[0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875,0.9947654997294875],[0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377,0.9944493554756377],[0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185,0.9941429382204185],[0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081,0.9938473498843081],[0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204,0.9935635822172204],[0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793,0.993292489079793],[0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531,0.9930347593649531],[0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512,0.9927908906107512],[0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492,0.9925611633398492],[0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542,0.9923456161764542],[0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954,0.9921440218429954],[0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604,0.9919558642432604],[0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097,0.9917803170283097],[0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726,0.9916162243681726],[0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072,0.9914620851840072],[0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809,0.991316042883809],[0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588,0.9911758836338588],[0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424,0.9910390470736424],[0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524,0.9909026535037524],[0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346,0.9907635502760346],[0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422,0.9906183773641422],[0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673,0.9904636488103673],[0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234,0.9902958441109234],[0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624,0.9901115021182624],[0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342,0.9899073095488342]],[[0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174,0.0025060408039606174],[0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792,0.002564774971484792],[0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367,0.0027289185487931367],[0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826,0.0029559586762367826],[0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901,0.003214557615069901],[0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781,0.003485440951762781],[0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764,0.003758169731712764],[0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774,0.004027766544196774],[0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058,0.004292246749057058],[0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846,0.004551039338142846],[0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659,0.004804092237873659],[0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415,0.0050514701160922415],[0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304,0.005293274598791304],[0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659,0.005529730629970659],[0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288,0.005761305495475288],[0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746,0.005988765342543746],[0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415,0.00621312166744415],[0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906,0.006435467465360906],[0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842,0.006656741269754842],[0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628,0.006877480208089628],[0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315,0.007097625428619315],[0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778,0.007316425460876778],[0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709,0.007532453965456709],[0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697,0.007743730482073697],[0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864,0.007947915069909864],[0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898,0.008142541873007898],[0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102,0.008325259409378102],[0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027,0.008494052322825027],[0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562,0.00864742698083562],[0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063,0.008784549721644063],[0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722,0.008905331116939722],[0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407,0.00901045254340407],[0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152,0.009101333324995152],[0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283,0.009180038580049283],[0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782,0.009249130532741782],[0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274,0.009311470094917274],[0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344,0.009369981280238344],[0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144,0.009427398173136144],[0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788,0.00948602168513788],[0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183,0.009547519402757183],[0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616,0.009612804204658616],[0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294,0.00968202373297294],[0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037,0.009754681574062037],[0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744,0.00982989198060744],[0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468,0.00990674583974468],[0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374,0.00998474250679374],[0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368,0.010064227406060368],[0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438,0.010146772941334438],[0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896,0.010235448837019896],[0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034,0.010334943248009034]],[],[],[[0.79348965166324,0.7931810251756211,0.7928866152922683,0.7926067000898634,0.7923415445963937,0.792091400196117,0.79185650406231,0.7916370786204158,0.7914333310440931,0.7912454527865308,0.7910736191492359,0.7909179888903229,0.7907787038741421,0.7906558887638677,0.7905496507584443,0.7904600793750481,0.7903872462779746,0.7903312051546034,0.7902919916388355,0.7902696232821301,0.7902640995720084,0.7902754019976309,0.7903034941618035,0.7903483219385196,0.7904098136749134,0.7904878804362774,0.7905824162925909,0.7906932986448155,0.7908203885890432,0.7909635313164268,0.7911225565466934,0.7912972789929252,0.7914874988552022,0.7916930023406286,0.791913562207216,0.792148938329063,0.792398878280259,0.7926631179349503,0.7929413820810222,0.7932333850448982,0.7935388313250056,0.793857416231525,0.7941888265301207,0.7945327410874354,0.7948888315162328,0.7952567628181721,0.7956361940223138,0.7960267788175643,0.796428166177393,0.7968400009752666],[0.7873152101697144,0.7869631030094115,0.7866270508127711,0.7863073864505195,0.7860044274619257,0.7857184752876802,0.7854498145370845,0.7851987122932951,0.7849654174602225,0.7847501601544982,0.7845531511457073,0.7843745813478369,0.7842146213646043,0.7840734210910294,0.783951109373276,0.7838477937284385,0.7837635601255799,0.7836984728289409,0.7836525743038548,0.7836258851855076,0.7836184043102852,0.7836301088090746,0.7836609542614985,0.7837108749097115,0.7837797839300387,0.7838675737604233,0.7839741164813502,0.7840992642476545,0.7842428497683819,0.7844046868316699,0.7845845708714456,0.7847822795725989,0.7849975735111873,0.7852301968261549,0.785479877919011,0.7857463301778994,0.7860292527225154,0.786328331166364,0.7866432383929296,0.7869736353424125,0.7873191718058028,0.7876794872231845,0.7880542114833069,0.7884429657216112,0.7888453631140616,0.7892610096643015,0.7896895049818227,0.7901304430490186,0.7905834129751621,0.7910479997355286],[0.780885756309152,0.7804855935379387,0.7801034684157527,0.7797397786324787,0.7793949039693798,0.7790692053064188,0.7787630236714616,0.7784766793368024,0.7782104709682618,0.7779646748318748,0.7777395440628841,0.7775353080014046,0.7773521715987138,0.7771903148976762,0.7770498925903051,0.7769310336549397,0.7768338410749447,0.7767583916402635,0.7767047358325485,0.776672897793998,0.7766628753794205,0.7766746402904683,0.7767081382904042,0.7767632894972348,0.77683998875253,0.7769381060627863,0.7770574871097731,0.7771979538259255,0.7773593050305363,0.7775413171222305,0.7777437448230005,0.7779663219689283,0.7782087623426189,0.7784707605423223,0.778751992882726,0.7790521183224428,0.7793707794133105,0.7797076032667434,0.7800622025325381,0.7804341763857203,0.7808231115172303,0.7812285831244747,0.7816501558980204,0.7820873850009518,0.782539817037685,0.7830069910092894,0.7834884392526338,0.7839836883609363,0.7844922600835534,0.7850136722030892],[0.7742744687750402,0.7738216775047821,0.7733890316921657,0.7729770053080411,0.7725860515652336,0.7722166016289759,0.7718690633774352,0.7715438202203391,0.7712412299835063,0.7709616238667907,0.7707053054825471,0.7704725499812308,0.7702636032701476,0.770078681330694,0.7699179696386675,0.7697816226914012,0.7696697636445962,0.7695824840608055,0.7695198437705784,0.769481870846317,0.7694685616879609,0.7694798812186802,0.7695157631878905,0.7695761105780615,0.7696607961110359,0.7697696628488848,0.769902524883725,0.7700591681104072,0.7702393510755736,0.7704428058962557,0.770669239240957,0.7709183333660357,0.7711897472001503,0.7714831174695709,0.7717980598572696,0.77213417018888,0.7724910256388562,0.7728681859504432,0.7732651946634042,0.773681580343806,0.774116857810547,0.7745705293537173,0.7750420859402816,0.775531008402992,0.7760367686088461,0.7765588306037995,0.77709665173084,0.777649683718892,0.778217373740383,0.7787991654356355],[0.7675764461351676,0.7670666535460815,0.7665792068568742,0.7661146691690661,0.7656735797751018,0.7652564524768478,0.7648637739617568,0.7644960022486547,0.7641535652149687,0.7638368592168882,0.7635462478134444,0.763282060604811,0.7630445921942584,0.7628341012821678,0.7626508098993177,0.7624949027853449,0.7623665269168568,0.762265791188161,0.7621927662460379,0.7621474844784072,0.7621299401551942,0.762140089718211,0.7621778522154448,0.7622431098738452,0.7623357088035305,0.7624554598253026,0.7626021394125126,0.7627754907376236,0.7629752248133105,0.7632010217176022,0.7634525318923948,0.7637293775046555,0.7640311538597644,0.7643574308567005,0.7647077544751437,0.7650816482850271,0.7654786149696069,0.765898137853713,0.7663396824294689,0.7668026978724309,0.7672866185417604,0.7677908654587097,0.7683148477583523,0.7688579641101223,0.7694196041033294,0.7699991495943904,0.7705959760130479,0.771209453625343,0.7718389487515658,0.7724838249378163],[0.7609103307914745,0.7603396402406062,0.759793539059954,0.7592726934357739,0.7587777426472408,0.7583092968677506,0.7578679350275607,0.7574542027558647,0.7570686104205114,0.7567116312833873,0.7563836997889462,0.7560852100024886,0.7558165142135534,0.7555779217182089,0.7553696977921314,0.7551920628641843,0.7550451918978055,0.754929213984933,0.7548442121545241,0.7547902233950173,0.7547672388874256,0.7547752044432088,0.7548140211387124,0.7548835461358407,0.7549835936767938,0.7551139362391867,0.7552743058366838,0.7554643954494482,0.7556838605682044,0.7559323208355349,0.7562093617681481,0.7565145365442267,0.75684736784057,0.7572073497050273,0.7575939494506484,0.7580066095590081,0.7584447495812706,0.7589077680266887,0.7593950442293846,0.7599059401853812,0.7604398023529396,0.7609959634102981,0.7615737439658693,0.7621724542168544,0.7627913955530441,0.7634298621033181,0.7640871422230117,0.7647625199208935,0.7654552762250125,0.766164690487103],[0.7544187173673151,0.7537840821221494,0.7531762519997959,0.752596010584911,0.7520441117055293,0.7515212765578119,0.7510281908843,0.7505655022331053,0.750133817326474,0.7497336995676148,0.7493656667145091,0.7490301887485415,0.7487276859641783,0.7484585273035493,0.7482230289567154,0.7480214532446482,0.7478540077976807,0.7477208450374748,0.7476220619656205,0.7475577002569754,0.7475277466509661,0.7475321336294914,0.7475707403659315,0.7476433939262108,0.7477498706999854,0.7478898980378594,0.7480631560691169,0.7482692796737447,0.7485078605824764,0.7487784495791338,0.7490805587805813,0.7494136639710525,0.7497772069693532,0.7501705980093925,0.7505932181165604,0.7510444214645831,0.7515235376995666,0.7520298742199578,0.7525627184030447,0.7531213397703752,0.7537049920860746,0.7543129153834651,0.7549443379166575,0.7555984780348683,0.7562745459781615,0.7569717455940841,0.7576892759753326,0.7584263330190959,0.759182110909156,0.7599558035221443],[0.7482665801784887,0.7475662940776651,0.7468949060539388,0.746253330126408,0.7456424484708427,0.7450631076848799,0.7445161150707651,0.7440022349761225,0.7435221852368088,0.7430766337686456,0.7426661953564659,0.7422914286891704,0.7419528336881318,0.7416508491731715,0.7413858509054081,0.7411581500396153,0.7409679920105663,0.740815555868513,0.7407009540689244,0.7406242327114108,0.7405853722129199,0.7405842883913374,0.7406208339279464,0.7406948001711345,0.7408059192394225,0.7409538663793774,0.7411382625331562,0.7413586770711281,0.7416146306469905,0.7419055981357384,0.7422310116184838,0.7425902633821853,0.742982708906593,0.7434076698149505,0.7438644367690684,0.7443522722931873,0.7448704135145064,0.7454180748113217,0.745994450362395,0.7465987165934524,0.7472300345186103,0.7478875519760849,0.7485704057587773,0.7492777236412903,0.7500086263056512,0.7507622291685305,0.7515376441130903,0.7523339811287952,0.7531503498626116,0.7539858610850206],[0.7426366755376367,0.7418709913445163,0.7411360563185783,0.740432923366489,0.7397626130157059,0.739126108672709,0.7385243518037766,0.7379582370915604,0.7374286076307074,0.7369362502353775,0.7364818909398939,0.7360661907799625,0.7356897419448184,0.7353530643893242,0.73505660298868,0.7348007253067012,0.7345857200318688,0.7344117961144739,0.7342790826147287,0.7341876292476213,0.7341374075875816,0.7341283128765355,0.7341601663639642,0.7342327180978712,0.7343456500811114,0.7344985797078718,0.7346910633993201,0.734922600364516,0.7351926364215479,0.7355005678235798,0.7358457450443077,0.7362274764866834,0.736645032087307,0.7370976467964077,0.7375845239197654,0.7381048383142701,0.738657739433142,0.7392423542202496,0.7398577898555747,0.7405031363557841,0.7411774690352204,0.7418798508334887,0.7426093345163005,0.7433649647564238,0.7441457801015312,0.7449508148355162,0.7457791007394967,0.7466296687582857,0.7475015505776299,0.748393780117005],[0.7377205701810938,0.7368924225078552,0.7360965005774196,0.7353339940434169,0.7346060620482994,0.7339138275383214,0.7332583713177933,0.7326407258882839,0.732061869138521,0.7315227179748204,0.7310241220092086,0.7305668574510331,0.7301516213743102,0.7297790265523196,0.7294495970570171,0.7291637648081227,0.7289218672221348,0.7287241460562849,0.728570747473049,0.7284617232777548,0.7283970332166474,0.7283765481747784,0.7284000540867905,0.7284672563685723,0.7285777846895404,0.7287311979280234,0.7289269891801109,0.7291645907208831,0.7294433788432914,0.7297626785226027,0.7301217678728402,0.7305198823761744,0.7309562188772616,0.7314299393426418,0.7319401743910925,0.7324860266047721,0.7330665736335122,0.7336808711060602,0.7343279553626958,0.7350068460236654,0.7357165484074396,0.736456055812051,0.7372243516717827,0.7380204116003617,0.7388432053306062,0.7396916985592447,0.740564854704407,0.741461636582118,0.7423810080070177,0.7433219353215341],[0.7337037942651832,0.7328194964791169,0.7319684124582961,0.7311518477231854,0.7303710813640804,0.7296273599081092,0.7289218907322724,0.7282558350163431,0.7276303002423707,0.7270463322695835,0.7265049070501118,0.7260069221095791,0.7255531880050131,0.7251444200934529,0.7247812310839771,0.7244641249587869,0.7241934928599578,0.7239696113802943,0.7237926433780757,0.7236626410688263,0.7235795508800983,0.723543219464408,0.7235534003241302,0.7236097606327356,0.7237118879730254,0.7238592968227529,0.7240514346950816,0.724287687891304,0.7245673868541141,0.7248898111282384,0.7252541939460208,0.725659726461634,0.7261055616607693,0.7265908179740201,0.7271145826223797,0.727675914722688,0.7282738481797395,0.7289073943902362,0.7295755447819472,0.7302772732094012,0.7310115382252342,0.7317772852440321,0.7325734486131634,0.7333989536027916,0.7342527183249804,0.7351336555896794,0.7360406747033617,0.73697268321429,0.737928588606779,0.7389072999454547],[0.7307443496353783,0.7298138622794049,0.7289170457231668,0.7280552796300388,0.727229920912652,0.7264422976449804,0.725693702477975,0.7249853855285648,0.7243185467103723,0.7236943274730441,0.7231138019157332,0.7225779672393496,0.7220877335030448,0.7216439126594698,0.7212472068986321,0.7208981966723601,0.7205973303779589,0.7203449204722256,0.7201411482647939,0.7199860732017944,0.7198796427544221,0.7198217017718641,0.7198120011295037,0.7198502056792169,0.719935901537789,0.7200686027549393,0.7202477574034594,0.7204727531339787,0.7207429222366537,0.7210575462517388,0.7214158601706019,0.7218170562681889,0.7222602876072213,0.7227446712534165,0.7232692912397297,0.7238332013159559,0.7244354275179777,0.725074970588495,0.7257508082782116,0.7264618975532594,0.7272071767311399,0.7279855675637709,0.7287959772824313,0.7296373006156326,0.7305084217873036,0.7314082164993019,0.7323355538992146,0.7332892985317951,0.7342683122702274,0.7352714562217368],[0.7289474710748803,0.7279835232369231,0.7270532003763259,0.7261579055131685,0.7252990199203676,0.7244778970465452,0.7236958559394147,0.7229541741396673,0.7222540800147315,0.7215967445022826,0.7209832722367263,0.720414692042657,0.719891946810478,0.7194158828576477,0.7189872391190995,0.7186066370729068,0.7182745731944908,0.717991416087732,0.7177574090262736,0.7175726764312041,0.7174372321067104,0.7173509877776312,0.7173137612791907,0.717325284172762,0.7173852087302869,0.7174931142919174,0.7176485130246397,0.7178508551190927,0.7180995334662935,0.7183938878585935,0.7187332087610507,0.7191167407008396,0.7195436853233919,0.720013204164575,0.7205244211882151,0.7210764251374744,0.7216682717468602,0.722298985858824,0.7229675634849833,0.72367297384699,0.7244141614261214,0.7251900480440208,0.7259995349899862,0.7268415052031414,0.7277148255111113,0.7286183489207967,0.7295509169517467,0.7305113619986741,0.7314985097068845,0.7325111813428],[0.7283471006331083,0.7273630565638114,0.7264120965814371,0.7254955961101005,0.7246149073665383,0.7237713533731732,0.7229662215523153,0.722200756911256,0.7214761548465326,0.7207935536234872,0.7201540266275459,0.7195585745389785,0.7190081176530834,0.7185034886462658,0.7180454261584603,0.7176345695958314,0.7172714555233157,0.7169565158973872,0.7166900782012287,0.7164723673370015,0.7163035089633125,0.7161835338789726,0.7161123830489892,0.7160899129207294,0.7161159007556784,0.7161900497810665,0.7163119940332746,0.7164813028177242,0.7166974847491799,0.7169599913650487,0.717268220325367,0.7176215182291953,0.718019183089716,0.7184604665204282,0.718944575692798,0.7194706751314903,0.7200378884164383,0.7206452998609992,0.7212919562317855,0.7219768685682217,0.7226990141486631,0.7234573386357296,0.7242507584175466,0.7250781631453429,0.7259384184528714,0.7268303688307023,0.7277528406194343,0.7287046450806097,0.7296845815023933,0.7306914402983467],[0.7289059467959619,0.7279138301080764,0.7269537748751317,0.7260270894744489,0.7251350577543169,0.7242789337105728,0.7234599359499816,0.7226792419896644,0.7219379824587122,0.7212372352869296,0.7205780199852958,0.7199612921413051,0.7193879382672342,0.7188587711473096,0.718374525827429,0.717935856375963,0.7175433335153636,0.7171974431834127,0.7168985860340611,0.7166470778368943,0.7164431506878087,0.7162869549068864,0.7161785614759715,0.7161179648587255,0.7161050860484472,0.7161397757008413,0.7162218172269834,0.7163509297430763,0.7165267707961152,0.7167489388070378,0.7170169751948909,0.7173303661671624,0.7176885441832792,0.7180908891209459,0.7185367291988926,0.7190253417342827,0.7195559538368649,0.7201277431616574,0.7207398388527384,0.7213913228073998,0.7220812313689124,0.7228085575178542,0.723572253581971,0.7243712344324909,0.7252043810910317,0.7260705446429385,0.7269685503421685,0.7278972017971619,0.7288552851414216,0.7298415731114799],[0.7305318038037891,0.7295414997202498,0.7285818473791955,0.7276540695408587,0.7267593650269726,0.7258989043885338,0.7250738255119336,0.7242852292101933,0.7235341748531736,0.7228216760970159,0.7221486967781163,0.7215161470399101,0.720924879761008,0.7203756873501751,0.7198692989669022,0.7194063782158363,0.7189875213493915,0.7186132559961866,0.7182840404145704,0.7180002632516772,0.7177622437705243,0.7175702324918176,0.7174244121843003,0.7173248991282379,0.717271744571127,0.7172649362927905,0.7173044001982224,0.7173900018602657,0.7175215479398553,0.7176987874185483,0.7179214125860638,0.7181890597345066,0.7185013095213063,0.7188576869760028,0.7192576611446638,0.7197006443952516,0.7201859914565554,0.7207129983437419,0.7212809014404655,0.7218888771369243,0.7225360424869836,0.7232214572410249,0.723944127319807,0.7247030094671111,0.7254970166403765,0.7263250237118106,0.7271858731686803,0.7280783806251081,0.7290013400475619,0.7299535286507761],[0.733097644601595,0.7321168294404261,0.73116501082566,0.730243323633461,0.7293528809602715,0.7284947707192244,0.7276700522428956,0.7268797529250368,0.7261248649361121,0.7254063420488654,0.7247250966105896,0.7240819966980478,0.7234778634890008,0.7229134688809034,0.7223895333825973,0.7219067242987761,0.7214656542198532,0.7210668798218669,0.7207109009725465,0.7203981601310102,0.7201290420201492,0.7199038735429565,0.7197229239071499,0.7195864049166961,0.7194944713843793,0.7194472216164335,0.719444697918448,0.719486887071141,0.71957372072503,0.7197050756643146,0.7198807738922219,0.7201005824924441,0.7203642132239418,0.7206713218091179,0.7210215068780603,0.7214143085340978,0.7218492065082172,0.7223256178719248,0.7228428942798404,0.7234003187169791,0.7239971022336705,0.7246323848803372,0.7253052425340663,0.7260146946257309,0.7267597113825336,0.7275392205832287,0.728352113849331,0.7291972524952066,0.7300734729594154,0.7309795918390736],[0.7364581484348216,0.7354923386270604,0.7345537553810169,0.7336434520443048,0.7327624630472311,0.7319118012262513,0.7310924551733382,0.7303053866318319,0.7295515279596685,0.728831779680727,0.7281470081443406,0.7274980433117382,0.7268856766862968,0.7263106594019996,0.7257737004814355,0.725275465271096,0.7248165740577207,0.7243976008651115,0.7240190724262986,0.7236814673213516,0.7233852152666103,0.7231306965367941,0.7229182414974777,0.7227481302218648,0.7226205921627566,0.7225358058481351,0.7224938985669023,0.7224949460100415,0.7225389718318243,0.7226259470956721,0.7227557895700193,0.7229283628411947,0.7231434752134788,0.7234008783722377,0.7237002657968494,0.7240412709311947,0.7244234651609036,0.7248463557252569,0.7253093838256452,0.7258119233708079,0.7263532809255328,0.7269326973294948,0.7275493510657906,0.728202363012709,0.7288908020047211,0.7296136906954647,0.7303700113915288,0.731158711678602,0.7319787097567485,0.7328288994523987],[0.740461955847344,0.7395144801414337,0.7385924382637657,0.7376968116826096,0.7368285658416679,0.7359886480029167,0.735177985113,0.734397481705497,0.7336480178511184,0.7329304471673314,0.7322455948980839,0.7315942560731554,0.7309771937552355,0.7303951373811101,0.7298487812013688,0.7293387828208391,0.7288657618395812,0.7284302985917623,0.7280329329771591,0.7276741633774606,0.7273544456470471,0.7270741921655651,0.7268337709375139,0.7266335047222579,0.7264736701765182,0.7263544969905726,0.726276166999259,0.7262388132496362,0.7262425190090576,0.7262873167008093,0.7263731867598295,0.7265000564089312,0.7266677983670771,0.7268762295162586,0.7271251095727513,0.7274141398315469,0.7277429620777507,0.7281111577817133,0.728518247709458,0.7289636920792423,0.7294468913731114,0.7299671878684473,0.7305238678954932,0.7311161647652651,0.7317432622618518,0.7324042985629664,0.733098370444612,0.7338245376355388,0.7345818272076389,0.7353692379128194],[0.7449610177045642,0.7440329539067841,0.7431285598381965,0.7422487553706665,0.7413944468966253,0.7405665255195651,0.739765865257829,0.7389933212688745,0.7382497281008142,0.7375358979775013,0.7368526191227487,0.7362006541284475,0.7355807383703805,0.7349935784744528,0.7344398508348678,0.7339202001845296,0.7334352382166497,0.7329855422552416,0.7325716539709335,0.732194078137375,0.7318532814225187,0.7315496912082808,0.7312836944316203,0.7310556364399772,0.7308658198544115,0.7307145034347351,0.7306019009425935,0.7305281800008793,0.7304934609511962,0.7304978157153713,0.7305412666722806,0.7306237855674214,0.7307452924795698,0.7309056548761103,0.7311046867956794,0.7313421482028264,0.7316177445635422,0.7319311266917267,0.7322818909141002,0.7326695795941993,0.7330936820449747,0.7335536358448861,0.7340488285556158,0.734578599822413,0.7351422438224917,0.735739012014389,0.7363681161327422,0.7370287313688332,0.7377199996771764,0.7384410331516138],[0.7498181557736581,0.7489083226204692,0.7480204452241661,0.7471553921242202,0.7463140204680626,0.745497174423966,0.7447056835964421,0.743940361448495,0.7432020037347853,0.7424913869493989,0.7418092667914936,0.7411563766516203,0.7405334261209848,0.739941099525375,0.7393800544849025,0.7388509205001648,0.7383542975649073,0.7378907548048175,0.7374608291417192,0.7370650239822147,0.7367038079297543,0.7363776135192571,0.7360868359737968,0.7358318319835178,0.7356129185079241,0.7354303716039728,0.7352844252840463,0.7351752704098447,0.7351030536305085,0.7350678763758004,0.735069793917828,0.7351088145174729,0.7351848986742074,0.7352979585001377,0.735447857240681,0.7356344089650235,0.7358573784492077,0.7361164812731987,0.7364113841504929,0.7367417055047912,0.7371070163031049,0.737506841148651,0.7379406596304113,0.7384079079196573,0.7389079805975433,0.7394402326924114,0.7400039819010427,0.74059851096492,0.7412230701707152,0.7418768799436251],[0.7549132909762875,0.7540183466874134,0.7531436985527271,0.7522901744390531,0.7514585925274331,0.7506497598649418,0.7498644709109337,0.7491035060807796,0.7483676302900146,0.7476575915016633,0.7469741192793219,0.7463179233483935,0.7456896921676812,0.7450900915133571,0.7445197630771762,0.743979323080668,0.7434693609069754,0.7429904377519896,0.7425430852965076,0.7421278044012934,0.7417450638272038,0.7413952989829171,0.7410789107033282,0.7407962640623098,0.7405476872243135,0.7403334703401707,0.7401538644934376,0.7400090807046855,0.7398992890022216,0.7398246175687951,0.739785151974836,0.7397809345096182,0.7398119636223712,0.7398781934857046,0.7399795336936885,0.7401158491065011,0.7402869598526518,0.740492641498423,0.7407326253923245,0.7410065991900915,0.7413142075631237,0.7416550530903805,0.7420286973307113,0.7424346620695619,0.7428724307310759,0.7433414499439309,0.7438411312469282,0.7443708529184583,0.744929961912562,0.7455177758834025],[0.7601484000641402,0.7592630466582752,0.7583963797405675,0.7575491981994159,0.7567222927244128,0.75591644444197,0.7551324235402441,0.7543709878860314,0.7536328816362929,0.7529188338469622,0.7522295570816755,0.7515657460230621,0.7509280760892325,0.7503172020581264,0.7497337567024218,0.7491783494377766,0.7486515649872774,0.7481539620651086,0.747686072082643,0.7472483978803809,0.7468414124894434,0.7464655579266516,0.74612124402759,0.7458088473224573,0.7455287099599475,0.7452811386848505,0.7450664038755218,0.744884738647793,0.7447363380322984,0.744621358232509,0.7445399159710036,0.7444920879316146,0.7444779103050527,0.7444973784454139,0.7445504466445736,0.7446370280308905,0.7447569945978332,0.7449101773671523,0.7450963666900289,0.7453153126882819,0.7455667258362293,0.7458502776822309,0.7461656017073093,0.7465122943166427,0.7468899159581445,0.747297992360894,0.7477360158848558,0.7482034469721872,0.748699715689498,0.7492242233497124],[0.7654511896099171,0.7645684526441049,0.7637028328716402,0.7628551133545809,0.7620260703968461,0.761216472222514,0.7604270776400042,0.7596586346948387,0.7589118793137583,0.7581875339430487,0.7574863061840205,0.7568088874286717,0.7561559514986587,0.755528153290805,0.7549261274324952,0.7543504869504232,0.7538018219563098,0.7532806983533531,0.7527876565673455,0.7523232103065738,0.7518878453547972,0.7514820184018118,0.751106155916293,0.750760653065816,0.7504458726891315,0.7501621443259496,0.7499097633096146,0.7496889899281658,0.7495000486593248,0.7493431274849462,0.7492183772903924,0.7491259113541355,0.7490658049326465,0.7490380949452893,0.7490427797635031,0.749079819108015,0.7491491340571935,0.7492506071689242,0.7493840827175836,0.7495493670468087,0.7497462290378292,0.7499744006921687,0.7502335778265387,0.7505234208767829,0.7508435558067849,0.7511935751173632,0.7515730389493545,0.7519814762743484,0.752418386165904,0.7528832391435467],[0.7707775619709192,0.7698891120696688,0.7690162358414085,0.7681597152653271,0.7673203271109962,0.766498841622038,0.7656960211823916,0.7649126189680663,0.7641493775874145,0.7634070277130831,0.7626862867089425,0.7619878572554234,0.7613124259768254,0.7606606620742937,0.7600332159682981,0.7594307179545715,0.7588537768776025,0.7583029788259013,0.7577788858533756,0.7572820347312773,0.7568129357352765,0.7563720714723221,0.7559598957520216,0.7555768325073337,0.755223274769401,0.7548995837013593,0.7546060876959341,0.7543430815415714,0.7541108256617453,0.7539095454319358,0.7537394305785694,0.7536006346639584,0.7534932746609742,0.7534174306208201,0.7533731454368573,0.7533604247069579,0.7533792366963497,0.7534295124023379,0.753511145721699,0.7536239937208897,0.7537678770085713,0.7539425802092685,0.754147852536315,0.7543834084615698,0.7546489284787475,0.7549440599565875,0.755268418077514,0.7556215868569104,0.7560031202376599,0.7564125432541963],[0.7761130373955104,0.7752095312945412,0.774320060009308,0.7734454207004782,0.7725864071125884,0.7717438082242409,0.7709184068763297,0.7701109783814646,0.7693222891179431,0.7685530951117916,0.7678041406105698,0.7670761566527946,0.7663698596369999,0.7656859498945945,0.7650251102708259,0.7643880047182856,0.7637752769075096,0.7631875488593326,0.7626254196037474,0.7620894638700858,0.7615802308133943,0.7610982427819085,0.7606439941305312,0.7602179500852035,0.7598205456630076,0.7594521846527569,0.7591132386607208,0.7588040462259777,0.7585249120097113,0.7582761060625338,0.7580578631736717,0.7578703823055386,0.7577138261168904,0.7575883205773817,0.7574939546759342,0.757430780224887,0.7573988117614293,0.7573980265473192,0.7574283646673788,0.7574897292267253,0.7575819866461563,0.7577049670545656,0.7578584647767259,0.7580422389142422,0.7582560140169663,0.758499480841671,0.7587722971943139,0.7590740888517911,0.7594044505586891,0.7597629470941835],[0.7814733225141631,0.7805447564998041,0.7796286616227007,0.7787258678289429,0.7778372038225004,0.7769634956395721,0.7761055651939162,0.7752642287966676,0.7744402956543788,0.7736345663492477,0.7728478313057023,0.7720808692477256,0.7713344456514868,0.7706093111980394,0.7699062002309909,0.769225829224215,0.7685688952647929,0.767936074556479,0.7673280209490693,0.7667453644991088,0.7661887100674016,0.76565863595879,0.7651556926096351,0.7646804013283747,0.7642332530944296,0.7638147074206045,0.7634251912839584,0.7630650981299185,0.7627347869541687,0.7624345814665737,0.76216476934108,0.7619256015552014,0.7617172918223093,0.7615400161195467,0.7613939123137454,0.761279079887273,0.7611955797652454,0.7611434342450543,0.7611226270286371,0.7611331033574081,0.7611747702492386,0.7612474968363608,0.7613511148025447,0.7614854189174062,0.7616501676652087,0.7618450839650545,0.7620698559789265,0.7623241380036234,0.7626075514422508,0.7629196858505969],[0.7869041738245173,0.7859402557958015,0.7849871808947451,0.7840458305465208,0.7831170876406441,0.7822018349835675,0.7813009537115708,0.7804153216678505,0.7795458117480232,0.7786932902185402,0.7778586150128097,0.7770426340100816,0.7762461833024163,0.775470085455298,0.7747151477676637,0.773982160537322,0.7732718953379051,0.7725851033136316,0.7719225134982708,0.7712848311647772,0.7706727362120964,0.7700868815956501,0.7695278918079653,0.7689963614158384,0.7684928536602929,0.7680178991254316,0.7675719944820736,0.7671556013118058,0.7667691450167948,0.7664130138203563,0.7660875578629084,0.7657930883975159,0.7655298770887847,0.7652981554183762,0.7650981141999063,0.764929903205452,0.7647936309053309,0.7646893643222495,0.7646171290003279,0.7645769090889204,0.7645686475405653,0.764592246421801,0.7646475673350259,0.7647344319490059,0.7648526226351012,0.7650018832057695,0.7651819197514111,0.7653924015711797,0.7656329621929553,0.7659032004773113],[0.792480613580007,0.7914711698560708,0.7904708261909579,0.7894805349401943,0.7885012533463065,0.7875339418215416,0.7865795621752739,0.7856390757904499,0.7847134417538218,0.7838036149451363,0.7829105440908374,0.7820351697882295,0.7811784225064061,0.7803412205706048,0.7795244681369602,0.7787290531649249,0.7779558453948833,0.7772056943387045,0.7764794272911641,0.7757778473702944,0.7751017315948175,0.7744518290068468,0.7738288588480275,0.7732335087972148,0.7726664332776537,0.7721282518414391,0.7716195476387796,0.7711408659792887,0.7706927129921471,0.7702755543915716,0.7698898143535313,0.7695358745091387,0.7692140730595514,0.7689247040166096,0.7686680165727775,0.7684442146032533,0.7682534563024181,0.7680958539560383,0.7679714738498994,0.7678803363147955,0.7678224159070428,0.7677976417229486,0.767805897844938,0.7678470239163393,0.7679208158411572,0.7680270266045199,0.7681653672088974,0.7683355077206286,0.7685370784208031,0.7687696710540876],[0.7983054322696919,0.797240871752136,0.7961834906848207,0.7951343320905149,0.7940944482443215,0.7930648987388659,0.792046748472099,0.7910410655624782,0.7900489191968464,0.7890713774169048,0.7881095048507445,0.7871643603964558,0.7862369948653718,0.7853284485930263,0.7844397490263958,0.7835719082964514,0.7827259207854709,0.7819027606989208,0.7811033796520539,0.7803287042816134,0.7795796338932399,0.7788570381552989,0.7781617548498989,0.7774945876918412,0.77685630422613,0.7762476338144761,0.7756692657209415,0.7751218473064982,0.7746059823418199,0.7741222294470755,0.7736711006668701,0.7732530601877655,0.7728685232050507,0.7725178549445695,0.7722013698445278,0.7719193309012421,0.7716719491818086,0.7714593835056485,0.7712817402958545,0.7711390736002139,0.7710313852807537,0.7709586253696248,0.7709206925881501,0.7709174350249042,0.7709486509677801,0.7710140898841472,0.7711134535424142,0.77124639726759,0.7714125313227991,0.7716114224081435],[0.8045067672262114,0.8033786287785655,0.80225549785317,0.8011385274622489,0.8000288854517651,0.7989277523063937,0.7978363188467634,0.7967557838239546,0.7956873514170284,0.7946322286401672,0.7935916226668199,0.7925667380790472,0.7915587740510758,0.7905689214768485,0.7895983600521256,0.7886482553224213,0.7877197557087408,0.7868139895237222,0.7859320619913461,0.7850750522838725,0.7842440105900697,0.7834399552291061,0.7826638698246837,0.7819167005540758,0.7811993534867065,0.780512692026736,0.7798575344738299,0.7792346517158562,0.7786447650666766,0.778088544261502,0.7775666056214358,0.7770795103978622,0.7766277633062526,0.7762118112577653,0.7758320422957201,0.7754887847426637,0.7751823065622873,0.7749128149389907,0.7746804560763487,0.7744853152142257,0.7743274168627546,0.7742067252499161,0.7741231449780038,0.7740765218828889,0.7740666440887025,0.774093243249349,0.7741559959671755,0.774254525378147,0.7743884028920341,0.7745571500754019],[0.811234386244628,0.8100359946237402,0.8088401042255109,0.8076479959270382,0.8064609725498224,0.8052803563738501,0.8041074865033933,0.8029437160893075,0.8017904094136857,0.8006489388438326,0.7995206816636578,0.7984070167917533,0.7973093213965966,0.7962289674205013,0.795167318025111,0.7941257239723859,0.7931055199561416,0.7921080209002671,0.7911345182407346,0.7901862762094163,0.7892645281385244,0.7883704728051425,0.7875052708358559,0.7866700411918311,0.7858658577548754,0.7850937460349924,0.7843546800197103,0.7836495791850232,0.7829793056871043,0.7823446617530536,0.7817463872878206,0.78118515771309,0.7806615820523767,0.7801762012748212,0.7797294869082741,0.7793218399301848,0.7789535899426383,0.7786249946356151,0.7783362395402255,0.7780874380713405,0.7778786318567157,0.7777097913474383,0.7775808167023546,0.7774915389370616,0.7774417213261504,0.7774310610456256,0.777459191040895,0.7775256821043686,0.777630045145592,0.7777717336359402],[0.8186541336798615,0.8173813832220616,0.8161082055199663,0.814836024289952,0.8135662941592879,0.8123004978804164,0.8110401433446595,0.8097867603991323,0.8085418974720142,0.807307118012798,0.806083996755668,0.8048741158157684,0.8036790606297943,0.8025004157540526,0.8013397605348969,0.8001986646682174,0.7990786836664272,0.7979813542531404,0.7969081897074233,0.795860675181105,0.7948402630141312,0.7938483680742839,0.7928863631487411,0.7919555744158877,0.7910572770264553,0.7901926908234513,0.7893629762303827,0.7885692303369821,0.7878124832109648,0.7870936944632807,0.7864137500928549,0.7857734596349655,0.7851735536351605,0.7846146814680313,0.7840974095172399,0.7836222197300038,0.7831895085558204,0.7827995862756182,0.7824526767238321,0.7821489174021716,0.7818883599801487,0.7816709711738535,0.7814966339910391,0.7813651493273787,0.7812762378958631,0.781229542468709,0.7812246304089263,0.7812609964668592,0.7813380658155646,0.781455197297852],[0.826939826689315,0.825592096583529,0.8242405043693074,0.8228866267815068,0.8215320825712662,0.8201785294443896,0.8188276607349831,0.8174812018158533,0.8161409062488325,0.8148085516799753,0.813485935486513,0.8121748701845258,0.8108771786085247,0.809594688876485,0.8083292291563656,0.8070826222527496,0.8058566800349158,0.8046531977304154,0.8034739481109915,0.8023206756004412,0.8011950903367068,0.8000988622230576,0.7990336150055779,0.7980009204163041,0.7970022924231206,0.7960391816288833,0.7951129698630999,0.7942249650098172,0.7933763961150252,0.7925684088158952,0.7918020611324494,0.791078319659803,0.7903980561959356,0.789762044836058,0.7891709595601131,0.788625372334813,0.7881257517460609,0.7876724621716323,0.7872657634978603,0.7869058113778113,0.7865926580222901,0.7863262535090595,0.7861064475900734,0.7859329919713994,0.7858055430359782,0.7857236649754729,0.7856868332943033,0.7856944386465269,0.7857457909645529,0.7858401238377284],[0.8362617518593101,0.8348429263557018,0.8334162303199426,0.831983396721241,0.8305462139327758,0.8291065224580436,0.8276662113189082,0.8262272141031032,0.8247915046706806,0.8233610925208301,0.8219380178226678,0.8205243461159776,0.8191221626905492,0.8177335666556699,0.8163606647145227,0.815005564661718,0.8136703686259366,0.8123571660836728,0.8110680266743113,0.8098049928512063,0.8085700724080016,0.8073652309240467,0.8061923841773274,0.8050533905777348,0.8039500436775711,0.8028840648198002,0.8018570959875071,0.800870692920166,0.7999263185634262,0.7990253369190886,0.7981690073605597,0.7973584794762908,0.79659478849943,0.7958788513761632,0.7952114635180489,0.7945932962752004,0.7940248951576259,0.793506678821681,0.7930389388276959,0.7926218401637783,0.7922554225198781,0.791939602285812,0.7916741752373352,0.7914588198658593,0.7912931013001802,0.7911764757627968,0.7911082954991142,0.7910878141150588,0.7911141922573195,0.7911865035704766],[0.8467708743025475,0.8452903878808741,0.8437974183416572,0.8422938492151177,0.8407816349839149,0.8392627976930485,0.8377394231444498,0.8362136566692596,0.8346876984723063,0.8331637985450351,0.8316442511451069,0.830131388843145,0.828627576139705,0.8271352026585188,0.825656675925478,0.8241944137467345,0.8227508362037433,0.8213283572881106,0.8199293762047802,0.8185562683783756,0.8172113762044484,0.8158969995948684,0.8146153863745912,0.813368722595345,0.8121591228402568,0.8109886206017312,0.8098591588227476,0.8087725806986613,0.8077306208421902,0.8067348969179973,0.8057869018547071,0.8048879967408339,0.8040394045066176,0.8032422044859634,0.8024973279414703,0.8018055546211666,0.8011675103983479,0.8005836660265215,0.8000543370206376,0.7995796846544266,0.7991597180427459,0.7987942972582314,0.7984831374141075,0.7982258136303181,0.798021766788684,0.7978703099747418,0.7977706354992886,0.797721822391248,0.7977228442549578,0.7977725773889006],[0.8585780600860614,0.8570518051292103,0.8555078802310212,0.8539483042361581,0.8523751841710443,0.8507907118257766,0.8491971598472242,0.8475968773324076,0.8459922849123158,0.8443858693174687,0.8427801774178265,0.8411778097311208,0.8395814133954129,0.8379936746037608,0.8364173105013628,0.8348550605486265,0.8333096773573564,0.8317839170118646,0.8302805288924484,0.8288022450255071,0.8273517689928005,0.8259317644421256,0.8245448432531324,0.8231935534251702,0.8218803667689377,0.8206076665000333,0.8193777348499531,0.8181927408279412,0.8170547282845101,0.8159656044431501,0.8149271290793161,0.8139409045335877,0.8130083667472972,0.8121307775025097,0.8113092180329616,0.8105445841482224,0.8098375829803738,0.8091887314224663,0.8085983562832258,0.8080665961358559,0.8075934047935228,0.8071785563031889,0.8068216513153844,0.8065221246618883,0.8062792539568909,0.806092169029841,0.8059598619989634,0.8058811978020184,0.8058549250135775,0.8058796867943298],[0.8717282367574971,0.8701790648756282,0.8686065743466104,0.8670128963524733,0.8654002683987323,0.8637710308766556,0.8621276230671772,0.860472578575304,0.858808520184703,0.8571381541228437,0.8554642637276758,0.85378970250729,0.852117386584419,0.850450286518074,0.8487914184950897,0.8471438348850762,0.8455106141533231,0.8438948501278448,0.8422996406192077,0.84072807539542,0.839183223519374,0.8376681200636455,0.8361857522275172,0.8347390448945349,0.8333308456866223,0.8319639095934398,0.830640883284054,0.8293642892423713,0.828136509907999,0.8269597720490709,0.8258361316405006,0.824767459565981,0.8237554284986914,0.8228015013368305,0.8219069215679323,0.821072705904201,0.8202996394669585,0.8195882737041578,0.8189389271090101,0.8183516886830726,0.8178264239686418,0.8173627833765661,0.8169602124659353,0.8166179637950169,0.8163351099563425,0.8161105574271984,0.815943060902319,0.8158312378207042,0.8157735828469243,0.8157684821143554],[0.8861707348399669,0.8846281896775795,0.8830564167346919,0.8814576337710401,0.8798341832148555,0.8781885285612854,0.87652325013244,0.8748410401931316,0.8731446974178358,0.8714371207054721,0.8697213023392647,0.8680003204891733,0.8662773310541235,0.8645555588406237,0.8628382880732215,0.8611288522307864,0.8594306232007978,0.8577469997417677,0.8560813952418068,0.854437224759266,0.852817891329686,0.8512267715222456,0.8496672002291453,0.848142454673609,0.84665573762762,0.845210159840851,0.8438087216999526,0.8424542941660164,0.8411495990824177,0.8398971890116016,0.8386994268543917,0.8375584656344441,0.8364762289927866,0.835454393118971,0.8344943710109973,0.8335973000470911,0.8327640338000475,0.8319951387842586,0.8312908964146684,0.8306513099686019,0.8300761159069436,0.8295647986349477,0.8291166076975938,0.8287305764742967,0.8284055415955859,0.8281401624879742,0.827932940622596,0.8277822381809176,0.8276862959542503,0.8276432503675002],[0.9017292020224981,0.9002281295692414,0.8986919272314883,0.897122877144947,0.8955234044757483,0.8938960733433559,0.8922435819885465,0.8905687571915674,0.8888745479486716,0.8871640184176216,0.8854403401443356,0.8837067835836534,0.8819667089271096,0.8802235562496994,0.8784808349859029,0.8767421127427021,0.8750110034541108,0.8732911548778313,0.8715862354301694,0.8698999203503536,0.8682358771799586,0.8665977505373842,0.8649891461612451,0.8634136141903106,0.8618746316412749,0.8603755840393528,0.8589197461506788,0.8575102617602086,0.8561501224352214,0.8548421452147057,0.8535889491741222,0.8523929308458761,0.8512562385612479,0.8501807460021213,0.8491680257992155,0.8482193251897537,0.8473355475598194,0.8465172447525302,0.8457646228757028,0.8450775596518879,0.8444556285057994,0.843898125198127,0.8434040946516821,0.842972356938442,0.8426015320408629,0.8422900632685107,0.8420362393161365,0.8418382149897703,0.8416940306424084,0.8416016303656477],[0.9180770953781822,0.9166550007018852,0.9151921632039545,0.9136909145550192,0.912153748251687,0.9105833146096604,0.908982414822255,0.9073539941091004,0.9057011339856861,0.9040270436889271,0.9023350507968582,0.9006285910819155,0.8989111976370288,0.8971864893120081,0.8954581584945706,0.8937299582659276,0.892005688955418,0.8902891841122584,0.8885842959054442,0.886894879955212,0.8852247795915348,0.8835778095269388,0.881957738922681,0.8803682738190419,0.8788130388922892,0.8772955584927459,0.8758192369103989,0.8743873378065672,0.8730029627423611,0.8716690287268801,0.8703882447004543,0.8691630868607323,0.8679957727327966,0.8668882338822164,0.8658420871960997,0.8648586049364675,0.8639386862392497,0.8630828422756438,0.8622912084576702,0.8615635736428352,0.8608994120624103,0.8602979140594614,0.859758015217774,0.8592784238965709,0.8588576472293444,0.8584940156467825,0.8581857059798633,0.8579307631946789,0.8577271208063505,0.857572620015793],[0.9347266465552104,0.9334201163727531,0.9320677707488717,0.9306719826018124,0.9292353065033295,0.9277604721045157,0.9262503763528046,0.9247080745630146,0.9231367704161316,0.9215398049670582,0.9199206447467159,0.918282869044566,0.916630156455184,0.9149662707671009,0.9132950462643793,0.9116203725016057,0.9099461786018569,0.9082764171151786,0.9066150474627225,0.9049660189794011,0.9033332535561398,0.9017206278719283,0.9001319551962359,0.89857096673443,0.8970412924831513,0.895546441560096,0.8940897819748244,0.892674519816737,0.8913036778579224,0.8899800736101584,0.8887062969502557,0.8874846875566208,0.8863173126091167,0.8852059455178701,0.8841520468557014,0.8831567490807112,0.8822208468349276,0.8813447943247655,0.880528710435746,0.8797723910825762,0.8790753273529366,0.8784367276112734,0.8778555418559472,0.8773304870142897,0.8768600722802663,0.8764426239336931,0.8760763093082873,0.8757591597190293,0.8754890922448785,0.8752639303129458],[0.9510388630339908,0.9498798286865315,0.9486706751624281,0.9474138131051497,0.9461118562184561,0.9447676121538,0.9433840717706351,0.941964396915812,0.9405119068879253,0.9390300637636091,0.9375224567654988,0.9359927858464338,0.9344448446524654,0.9328825030099458,0.9313096890607623,0.9297303711465793,0.9281485395190947,0.9265681879304303,0.9249932951370669,0.9234278063332443,0.921875614516439,0.9203405417791616,0.9188263205186066,0.917336574559449,0.9158748001961863,0.9144443471808982,0.9130483997114938,0.9116899575156848,0.9103718171782705,0.9090965539242573,0.9078665041465168,0.9066837490499564,0.9055500998659444,0.9044670851575595,0.9034359407703045,0.9024576029655539,0.9015327051917515,0.9006615787994221,0.899844257805398,0.8990804875886188,0.8983697371911515,0.8977112147351267,0.8971038853674593,0.8965464911108708,0.896037572020468,0.8955754881020814,0.8951584415238912,0.8947844987325384,0.8944516121599495,0.8941576412730831],[0.9662593849705435,0.9652721196674877,0.9642314827670985,0.96313992674296,0.9620001307999,0.9608149875729052,0.9595875875511277,0.9583212015794617,0.9570192618235333,0.9556853415919414,0.9543231343944202,0.9529364325803544,0.9515291058539659,0.950105079906188,0.9486683153440034,0.9472227870404549,0.945772463976329,0.9443212896003025,0.9428731626998993,0.9414319187517365,0.9400013117067058,0.9385849961634375,0.9371865098912606,0.9358092566808245,0.9344564895255945,0.9331312941692671,0.9318365730912749,0.9305750300432303,0.9293491552912813,0.9281612117604364,0.9270132223139549,0.9259069584304765,0.9248439305601773,0.9238253804452634,0.922852275676857,0.9219253067281337,0.9210448866527207,0.920211153570143,0.9194239759809658,0.9186829608691283,0.9179874644645462,0.9173366054616544,0.9167292804244259,0.9161641810587965,0.9156398130007342,0.9151545157519911,0.9147064833941492,0.9142937857223847,0.9139143894608371,0.9135661792488717],[0.9795819338752171,0.9787813700065514,0.9779256776869397,0.977017371678066,0.9760592199957487,0.9750542230661189,0.9740055895816815,0.9729167099964215,0.9717911286205525,0.9706325152116888,0.9694446368336607,0.9682313305933479,0.9669964776931643,0.9657439790702301,0.9644777327447063,0.9632016128760628,0.9619194504301005,0.960635015291606,0.9593519996162047,0.9580740021976384,0.9568045136304264,0.9555469020689145,0.9543043994186738,0.9530800878413498,0.9518768865058117,0.9506975385737015,0.949544598463032,0.9484204194868089,0.9473271420122528,0.9462666823281344,0.9452407224411628,0.9442507010458839,0.9432978059250241,0.9423829680377338,0.9415068575415304,0.9406698819697659,0.93987218675087,0.9391136582094916,0.938393929134624,0.9377123869380812,0.9370681843607616,0.9364602526168755,0.9358873168006604,0.9353479133189936,0.9348404090594199,0.9343630219588889,0.933913842605766,0.933490856487837,0.9330919664926682,0.9327150152738147],[0.9902403828209791,0.9896318769043013,0.9889686786914204,0.9882534134008278,0.9874889873682002,0.9866785513594398,0.9858254594611539,0.9849332263933083,0.9840054856070168,0.9830459498901734,0.9820583755857373,0.9810465310103488,0.9800141692578963,0.9789650052697842,0.9779026968326692,0.9768308290104905,0.9757529014206845,0.9746723177174854,0.9735923766421687,0.972516264035113,0.9714470452705262,0.9703876576640692,0.9693409025082182,0.9683094365021248,0.9672957624547104,0.9663022192459991,0.9653309711276994,0.9643839965271778,0.9634630765878794,0.9625697837336783,0.9617054705852877,0.9608712595846546,0.960068033699117,0.9592964285817216,0.9585568265578376,0.9578493527906619,0.9571738739488949,0.9565299996577322,0.9559170869585762,0.9553342479330172,0.9547803605629552,0.9542540828028427,0.953753869734863,0.953277993568039,0.9528245661339068,0.9523915634313824,0.9519768516893993,0.9515782143544161,0.9511933793764842,0.9508200461652908],[0.9976330326180827,0.9972134456069592,0.9967427939246212,0.9962238901197426,0.9956598376602402,0.9950539588282473,0.9944097256526846,0.9937306974657261,0.9930204663960945,0.9922826113799568,0.9915206608992834,0.9907380643376719,0.9899381715178794,0.9891242196634187,0.9882993267373409,0.9874664898849147,0.9866285875674463,0.9857883839352801,0.9849485340499035,0.984111588717077,0.9832799979142363,0.9824561120592715,0.981642180645431,0.9808403480322418,0.9800526464146655,0.9792809861797082,0.9785271439974724,0.9777927490850616,0.9770792681347726,0.9763879894228755,0.9757200066225893,0.9750762028438661,0.9744572354204212,0.9738635219654621,0.9732952282233717,0.9727522582538823,0.9722342474935742,0.9717405592398011,0.9712702850845436,0.9708222497790223,0.9703950209229134,0.9699869237359645,0.9695960609812828,0.9692203378732911,0.9688574915337406,0.9685051242798287,0.9681607397702404,0.9678217808298208,0.9674856676502905,0.9671498350415088],[1.0014869470897054,1.001246954257477,1.0009638126179732,1.0006404476482738,1.0002800158181013,0.9998858195652975,0.9994612245290254,0.9990095841774969,0.9985341747887078,0.9980381429725249,0.9975244673231681,0.9969959349896464,0.9964551329327516,0.9959044525397739,0.9953461052793671,0.9947821463543092,0.9942145029310011,0.9936450035035047,0.993075405256856,0.9925074168756296,0.9919427150205616,0.9913829535584262,0.9908297654475842,0.9902847578362434,0.9897495013541717,0.9892255147674849,0.9887142461674756,0.988217051748071,0.9877351730581948,0.9872697134434808,0.9868216142450801,0.9863916312153711,0.9859803115462468,0.9855879718863477,0.9852146777498137,0.9848602247918243,0.9845241225457669,0.9842055813803969,0.9839035036307116,0.9836164800554448,0.9833427929264231,0.9830804270870765,0.9828270901452986,0.9825802425240595,0.9823371373717821,0.9820948694052916,0.9818504307693731,0.9816007711338269,0.9813428586819686,0.9810737384895514],[1.0020287093983098,1.0019554725134037,1.001850007018565,1.0017152419046425,1.0015542387452814,1.001370116640682,1.0011659686429775,1.000944774993773,1.000709319840368,1.0004621197474988,1.0002053733182588,0.9999409395482783,0.9996703472650079,0.999394831568853,0.9991153893062035,0.9988328452438264,0.9985479218898455,0.9982613068194836,0.9979737114002415,0.9976859149485044,0.9973987901441381,0.9971133092852027,0.9968305347829776,0.9965515990282917,0.996277678254014,0.9960099635672371,0.9957496309943301,0.9954978115029116,0.9952555614675698,0.9950238337851992,0.9948034497135534,0.994595071441238,0.994399175367448,0.9942160260609016,0.9940456508756911,0.9938878152306665,0.9937419986224826,0.9936073715708894,0.9934827739490613,0.9933666956421103,0.993257261368144,0.9931522229237815,0.993048963878015,0.9929445228235874,0.9928356400602001,0.992718828454816,0.992590464149073,0.9924468894117268,0.9922845187106311,0.992099938678806],[0.9999030808234651,0.9999842413243117,1.000044064866523,1.0000853290517429,1.0001108661181526,1.0001234929502005,1.000125933431746,1.0001207339880962,1.0001101729873882,1.0000961646480107,1.0000801622465836,1.000063119398147,1.0000455564572428,1.000027652952865,1.0000093383809316,0.9999903815281727,0.9999704789838633,0.9999493434291311,0.9999267922254638,0.9999028303613954,0.9998776809693405,0.9998517563713161,0.9998256205805139,0.9997999531408599,0.9997755142987039,0.9997531114307511,0.9997335666494218,0.999717685504975,0.9997062267026076,0.9996998727522063,0.9996992014680397,0.99970465823552,0.9997165289619655,0.9997349136280196,0.9997597003560508,0.9997905399113258,0.9998268205510695,0.9998676431356838,0.9999117964153743,0.9999577324042321,1.0000035417525293,1.0000469290264657,1.0000851878049808,1.0001151798186112,1.0001333665902525,1.0001359212718182,1.0001188591482768,1.0000781690635236,1.0000099459865166,0.9999105252058812]],[[0.08536583391667761,0.08526710377692905,0.08517947810586263,0.08510317121214736,0.08503837016432145,0.08498523366109083,0.08494389105026058,0.0849144415075575,0.08489695338507931,0.08489146373739924,0.08489797803149206,0.08491647004466255,0.08494688195258306,0.08498912460742226,0.08504307800391013,0.08510859192908049,0.0851854867893918,0.08527355460699644,0.08537256017513736,0.08548224236102787,0.08560231554315266,0.08573247116871688,0.08587237941600462,0.0860216909456766,0.08618003872455725,0.0863470399052256,0.08652229774472481,0.08670540354593448,0.08689593860558903,0.08709347615355069,0.08729758326874824,0.08750782275813314,0.0877237549860678,0.08794493964271984,0.08817093744126148,0.08840131173494936,0.08863563004644957,0.08887346550307279,0.08911439817285866,0.08935801629769043,0.0896039174208117,0.08985170940724484,0.09010101135666566,0.09035145440926337,0.09060268244600324,0.09085435268550786,0.09110613618048015,0.09135771821720767,0.09160879862221241,0.09185909198054963],[0.08149875398584801,0.08136969980121762,0.08125486153869137,0.08115454660207118,0.08106902441942566,0.08099852459997152,0.08094323532298699,0.08090330198011299,0.0808788260896544,0.08086986449834038,0.08087642888249746,0.08089848555680236,0.08093595559479684,0.08098871526124411,0.08105659675228631,0.08113938923531117,0.08123684017654512,0.08134865694074639,0.08147450864404822,0.0816140282380706,0.08176681480092461,0.08193243600872446,0.08211043075971677,0.0823003119221497,0.08250156917652808,0.08271367192292214,0.08293607222448404,0.08316820775924114,0.0834095047535336,0.08365938087208909,0.08391724804162826,0.08418251518701043,0.08445459086120405,0.08473288575274454,0.08501681505677036,0.08530580069816066,0.08559927339768919,0.08589667457442442,0.08619745807980986,0.08650109176093249,0.08680705885240297,0.08711485919802162,0.08742401030497593,0.08773404823470518,0.08804452833577456,0.08835502582512869,0.08866513622494625,0.08897447566300362,0.08928268104498498,0.08958941010755828],[0.07700869772947122,0.07683980293595996,0.07668905103987778,0.07655688917383863,0.07644371125820681,0.07634985489807611,0.0762755986480939,0.07622115968777497,0.07618669194486856,0.07617228469827103,0.07617796168504631,0.07620368072849455,0.07624933389609584,0.07631474818775842,0.07639968674636329,0.07650385057433842,0.07662688073214845,0.07676836098735171,0.07692782087644354,0.07710473913621531,0.0772985474569285,0.07750863450630434,0.07773435017118942,0.07797500996277218,0.078229899531344,0.07849827923775084,0.0787793887307583,0.07907245148243931,0.0793766792372459,0.07969127633451363,0.08001544386861498,0.08034838365569845,0.08068930198078915,0.08103741310386582,0.08139194250827184,0.08175212987936703,0.08211723180562452,0.08248652419835356,0.08285930442985921,0.08323489319309499,0.08361263608872439,0.0839919049479663,0.08437209890167788,0.08475264520783019,0.08513299985088324,0.08551264792759017,0.08589110383448194,0.08626791127273534,0.08664264308633302,0.08701490094942174],[0.07185910198164103,0.07163752492031043,0.07143902201495655,0.0712642555929308,0.07111381309501484,0.07098820164223986,0.07088784319253426,0.07081307037789814,0.07076412310321822,0.07074114597564068,0.07074418661891554,0.07077319491073687,0.07082802316335672,0.0709084272492385,0.07101406865488062,0.07114451742782048,0.0712992559648509,0.07147768357418567,0.07167912173118096,0.07190281993660037,0.07214796207854093,0.07241367319412187,0.07269902652485713,0.07300305076015727,0.07332473736640512,0.07366304790422697,0.07401692124357055,0.07438528059462818,0.07476704028210844,0.07516111220048098,0.07556641189824104,0.07598186424964497,0.07640640868248043,0.0768390039400334,0.07727863236432636,0.07772430369579966,0.07817505839181779,0.07862997047265957,0.07908814990899149,0.07954874456924887,0.08001094174890308,0.08047396930633394,0.08093709643202318,0.08139963407911459,0.08186093508412853,0.0823203940068486,0.08277744671819606,0.08323156976433889,0.08368227953442102,0.0841291312581963],[0.06603824740962798,0.0657463730441847,0.0654837117390759,0.06525126797755489,0.06504994082667745,0.06488051395142344,0.06474364656940604,0.06463986555431031,0.06456955887857775,0.06453297056053885,0.06453019724890913,0.06456118653942748,0.06462573707599262,0.06472350044376297,0.06485398481634222,0.06501656027542196,0.06521046568100751,0.06543481693530581,0.06568861645481797,0.06597076364406805,0.0662800661511348,0.0666152516797414,0.06697498013465583,0.06735785588581401,0.06776243995087415,0.06818726191466636,0.06863083142598918,0.0690916491361942,0.06956821696886147,0.07005904763460986,0.07056267332887028,0.0710776535726372,0.07160258217633073,0.07213609332465806,0.07267686679560292,0.07322363233937908,0.07377517325343237,0.07433032919751217,0.07488799829866814,0.07544713859997791,0.07600676890913956,0.07656596910399435,0.07712387995183212,0.07767970249818484,0.07823269707893113,0.07878218200709798,0.07932753198290164,0.07986817627244944,0.0804035966972412,0.08093332547324188],[0.059575683713118555,0.059188869950134095,0.05883877707132503,0.058526974610431104,0.058254885696510106,0.05802376760582276,0.05783469371509493,0.05768853737749067,0.05758595821676732,0.057527391283768554,0.057513039443722415,0.05754286926585865,0.05761661057364874,0.057733759690977,0.05789358629419642,0.05809514365993364,0.05833728199079631,0.058618664411757386,0.05893778516321018,0.05929298947483902,0.059682494587848973,0.060104411400250565,0.060556766237830705,0.0610375222981461,0.06154460037182672,0.062075898510022265,0.0626293103746526,0.06320274207545261,0.06379412736161272,0.06440144109388299,0.065022710973876,0.06565602755024035,0.06629955255620136,0.06695152565998634,0.06761026972946083,0.06827419472571715,0.06894180034828779,0.06961167755802583,0.07028250910341759,0.07095306917297026,0.07162222229110372,0.07228892156827123,0.07295220640837759,0.07361119976836124,0.07426510505639493,0.07491320274678812,0.0755548467815249,0.0761894608205781,0.07681653439578472,0.07743561901620222],[0.05256885309925692,0.052051921238091665,0.051580514909776935,0.0511571754590557,0.050784252476670656,0.05046386349362235,0.05019785508482173,0.04998776680448015,0.049834799397584964,0.049739788659245165,0.04970318614147989,0.04972504764071972,0.049805030055713274,0.04994239681125899,0.05013603163156086,0.0503844600536494,0.0506858777293329,0.051038184299818996,0.05143902145684455,0.05188581373311357,0.05237581058773159,0.0529061284553244,0.05347379159124984,0.05407577074809069,0.05470901893932997,0.05537050376636249,0.056057235990460856,0.056766294212137476,0.05749484567101452,0.05824016329798771,0.05899963923911736,0.05977079513020714,0.060551289436429824,0.06133892218708591,0.06213163743602528,0.06292752376747514,0.06372481314848624,0.06452187840581998,0.06531722957913262,0.0661095093754727,0.06689748792365387,0.06768005700180552,0.06845622388789804,0.06922510496154288,0.06998591916601477,0.07073798142220891,0.07148069607104317,0.07221355040750539,0.072936108357955,0.07364800434224694],[0.045229472615665296,0.04453163062800684,0.043888500838145765,0.04330434492895806,0.042783227962879436,0.04232893134140475,0.04194486272949526,0.04163396691406923,0.041398642205672735,0.041240667280206804,0.04116114318397718,0.04116045453961213,0.041238252822940705,0.04139346304884427,0.041624313495438096,0.04192838643435337,0.04230268643433955,0.042743721827498374,0.043247594453785496,0.04381009282489619,0.04442678429522764,0.045093102571209444,0.04580442779163526,0.0465561573427685,0.04734376643346462,0.04816285818335798,0.04900920354128149,0.04987877174880858,0.050767752310939884,0.05167256955847597,0.05258989091386186,0.05351662993241714,0.054449945108126,0.05538723532692013,0.05632613273495868,0.057264493674706145,0.05820038823390848,0.059132088855369136,0.060058058370278944,0.06097693774493995,0.06188753376942709,0.06278880686595102,0.0636798591531312,0.0645599228687195,0.06542834922625747,0.06628459775955571,0.06712822619173267,0.06795888085199164,0.06877628765262087,0.06958024363028933],[0.037969412797105515,0.037019512359189814,0.03613033011344991,0.03530906391914734,0.03456295487932195,0.033899115593457846,0.03332432456669251,0.03284479400884514,0.03246592384911189,0.03219206009552061,0.032026279345500466,0.03197022195008448,0.03202399316799596,0.03218614467062794,0.032453739143084956,0.03282249049078423,0.03328696353550095,0.033840811767138504,0.0344770303774211,0.035188204024398845,0.035966733399165084,0.03680503028379645,0.03769567619304339,0.0386315441028892,0.0396058858654386,0.04061238972227134,0.041645213090340666,0.04269899580966913,0.04376885859862469,0.0448503907901141,0.0459396306813722,0.047033041120347174,0.048127482325171084,0.04922018341000557,0.0503087136712849,0.051390954363226896,0.05246507144619709,0.05352948961101261,0.0545828677525947,0.055624075975462206,0.05665217415156982,0.05766639201010066,0.058666110713017944,0.05965084585493525,0.06062023181780931,0.06157400740768229,0.06251200270044648,0.06343412702518059,0.06434035801617709,0.06523073166780645],[0.031553033938240375,0.030269311497632692,0.029039133914373388,0.0278732850231789,0.02678365225021034,0.025783111473694206,0.02488527460617691,0.024104060478638775,0.023453065030985463,0.02294474186800764,0.022589458669601856,0.022394556626907546,0.02236358375037092,0.022495869676791423,0.022786546163854834,0.023227011311890058,0.023805729852667823,0.024509199587604783,0.025322912334351053,0.02623218275379566,0.02722278097507779,0.028281359680829073,0.02939570126212064,0.030554825747273272,0.03174900132527637,0.03296969307078501,0.03420947686336934,0.03546193727011464,0.03672156149428417,0.03798363659864992,0.03924415386714712,0.040499722015409176,0.04174748965477118,0.04298507667699226,0.044210513853653065,0.04542218979353857,0.046618804379894456,0.04779932785772827,0.048962964822738125,0.0501091224563262,0.05123738244334655,0.052347476094407444,0.05343926226989897,0.05451270776766244,0.055567869890690604,0.056604880956355456,0.05762393454553018,0.05862527331980398,0.059609178258915305,0.06057595918959877],[0.02725108791491774,0.02561520598433905,0.024000220565242442,0.022415464986833868,0.02087254836622886,0.01938600928242873,0.017974105922801076,0.016659675306173422,0.015470853577223845,0.014441196287355504,0.013608402278545477,0.013010674704002297,0.012680322651776217,0.01263598514642173,0.012876957563625814,0.013383026929475902,0.014119975729696404,0.015047483352310202,0.016125800290104346,0.01731961922891914,0.018599463035635387,0.019941577284002615,0.021327170607033596,0.022741499075509014,0.02417302062842795,0.025612693574505702,0.027053423595443944,0.028489638268086582,0.029916962791320414,0.031331972997128164,0.032732006280950215,0.03411501560173164,0.03547945547244785,0.036824191787520215,0.038148429522964565,0.03945165395384057,0.04073358220537045,0.04199412280481515,0.04323334151863318,0.0444514322081022,0.045648691763108026,0.0468254984117505,0.0479822928768478,0.04911956197671226,0.05023782435925201,0.05133761812472978,0.05241949014007617,0.05348398688155126,0.05453164666647115,0.05556299315148919],[0.02646331904526456,0.024660271087677873,0.022846577640754328,0.021024437585829458,0.019196404953089597,0.017365528949343106,0.015535590194674775,0.013711519834960974,0.011900187807908547,0.010111990999854013,0.008364323461347778,0.006689892569124406,0.005158468922591062,0.003933548144179389,0.003354751188555426,0.003718822800038419,0.004799836276823784,0.0062198933023482495,0.007781567866361497,0.009401544284194787,0.011042229397197765,0.01268463644574562,0.014318168334254783,0.01593643792321267,0.01753538548616495,0.019112353163718145,0.02066559339268983,0.022193989083829187,0.023696883730581014,0.025173971674037923,0.026625222811385386,0.028050827833232626,0.0294511561640129,0.030826722065948692,0.03217815621164501,0.03350618110126464,0.03481158933969586,0.03609522417917276,0.03735796197373857,0.03860069634079194,0.03982432391527513,0.04102973163424301,0.04221778551645899,0.04338932091177001,0.044545134194088995,0.04568597586399668,0.04681254501525941,0.04792548510619532,0.04902538096344824,0.05011275693353508],[0.02935647508028262,0.02766458205371574,0.025966336808410727,0.0242641719803456,0.022560876717149125,0.02085970450978592,0.01916453458788449,0.01748012003807066,0.01581248021998862,0.014169540186108253,0.012562204680676441,0.011006213633054809,0.009525409935202782,0.008157453793874192,0.0069630314555952,0.006036413279733471,0.005501320437810659,0.005458336312509536,0.0059019947180342525,0.006721282406323296,0.007784452289004182,0.008992758188665068,0.010283877810025311,0.011620248492707364,0.012979109671047862,0.014346377380806737,0.015713157760680645,0.017073769479001227,0.01842459515483559,0.019763391111730536,0.021088856440238442,0.02240035306608346,0.023697716486560678,0.024981122669507423,0.02625099087376055,0.02750791023966773,0.028752582704940542,0.02998577760282057,0.031208294998457033,0.03242093586288816,0.03362447782835972,0.03481965566510948,0.036007145860039114,0.03718755481945848,0.03836141029837611,0.039529155702056194,0.04069114692796858,0.04184765142856708,0.04299884918435074,0.044144835286518],[0.03457830196401563,0.03310130567334497,0.0316269236361579,0.030157932207452526,0.02869740535633911,0.027248763463469456,0.025815834267477994,0.024402929158258396,0.023014938620594574,0.02165745106916926,0.020336899210983226,0.01906073667076695,0.01783764350671574,0.01667774998521896,0.015592849831958147,0.014596542597018584,0.013704197331259306,0.012932574016155322,0.012298906493843496,0.01181930674498736,0.011506571584196457,0.01136785243768316,0.011402982360275541,0.011604203516407554,0.01195747999823648,0.012444866969522638,0.013047062201446392,0.013745444681619392,0.014523329867324419,0.015366515037164309,0.01626333373556871,0.017204437030630546,0.018182458936610833,0.019191659740310833,0.02022759442915604,0.021286825125971427,0.022366681406294563,0.02346506542210533,0.024580296176607962,0.025710986843513604,0.026855949475515162,0.028014122188322027,0.029184514664384462,0.030366168492540948,0.0315581294251318,0.03275942910387235,0.03396907419976717,0.03518604124858725,0.03640927575489715,0.0376376943923649],[0.04067843195348599,0.03938720430596551,0.03809797918124075,0.03681236039168974,0.035532003698046925,0.03425861455079758,0.03299394626583151,0.03173979908111583,0.03049802071127208,0.0292705092300771,0.02805921937022567,0.02686617363411877,0.025693479950979845,0.024543357975696335,0.023418176469761975,0.022320504478550187,0.02125317913179471,0.02021939270059318,0.019222800810021066,0.018267652056677366,0.017358936140312902,0.016502542178436715,0.015705410165486995,0.014975645807548966,0.014322552601985577,0.013756518332138581,0.013288684576473916,0.012930341973918482,0.012692047065023448,0.012582552496070857,0.012607753921979844,0.012769921862880028,0.01306744276337386,0.013495137546813907,0.014045036131888572,0.014707366380542854,0.015471513454730558,0.016326789076157228,0.01726295385815967,0.018270511990001393,0.019340833248978208,0.020466162285806274,0.02163956451402555,0.02285484309078651,0.024106448257105912,0.025389390617450124,0.02669916367503019,0.02803167728504092,0.029383201772060694,0.0307503215924851],[0.046793798551387336,0.045635898017927855,0.044474688312588634,0.043310684652118146,0.0421443531454428,0.04097610314746887,0.03980627997246631,0.03863515825646252,0.03746293631260682,0.03628973188130484,0.035115579737635814,0.03394043168236875,0.032764159511292176,0.031586561634332606,0.030407374108434453,0.029226286969159986,0.028042966916049336,0.02685708765777983,0.025668369603056646,0.024476631163577078,0.0232818548231873,0.022084272482901048,0.0208844766569662,0.01968356723687109,0.018483348305831173,0.017286596667574927,0.016097434399303216,0.01492185293523942,0.013768456036695683,0.01264950925116267,0.011582385924863213,0.010591429135782848,0.009709969775593928,0.008981516059815705,0.008457849516944083,0.00819091093442011,0.008218028190982395,0.008547688217078698,0.009157095922905107,0.010003405059224767,0.011038734322489682,0.012220040959449934,0.013512604851946896,0.014889783919357504,0.01633146736286628,0.01782243344727692,0.019351008312131723,0.020908072870939407,0.022486356730531957,0.02407994341258976],[0.052529996489157786,0.05146702206202804,0.05039507119690911,0.049314016946255805,0.04822366885643608,0.04712376917560216,0.04601398968065771,0.04489392926115931,0.04376311239998329,0.0426209886886954,0.04146693350926263,0.04030025000270031,0.039120172429355046,0.037925871004978295,0.036716458272108114,0.035490997038492775,0.03424850988469612,0.03298799021337217,0.03170841478512076,0.030408757662895705,0.029088005471731966,0.027745173876988456,0.02637932519772059,0.024989587110194163,0.023575172473064815,0.022135400443439614,0.020669719294798338,0.01917773177712455,0.01765922464695088,0.01611420550584241,0.014542953151011334,0.012946094284890262,0.011324735006022081,0.00968071569254594,0.008017174855934062,0.006340006005965061,0.004662477044007129,0.003025064100919402,0.0016310693052349853,0.0015715642639852164,0.002958358612745615,0.0046524427963031394,0.006422935251600678,0.008224900312507357,0.010043277276749881,0.011870764450630204,0.013702806874710462,0.015536051222520535,0.017367764121797868,0.019195580270820294],[0.05775347079241324,0.056764983614509774,0.05576338732376291,0.05474829036474891,0.05371925766495867,0.05267581121941114,0.051617431448178756,0.05054355941835938,0.049453600022983366,0.04834692621007521,0.04722288435614842,0.04608080088058819,0.04491999020180498,0.04373976414431505,0.04253944292018001,0.04131836783149758,0.04007591587695276,0.03881151650045553,0.03752467080154948,0.03621497364688089,0.03488213929598768,0.03352603140723859,0.03214669865729177,0.030744417745409314,0.02931974634820993,0.027873589775711954,0.026407286870086276,0.02492272342882676,0.02342248568227782,0.021910073018606244,0.020390199690172937,0.018869231948024683,0.01735583327485437,0.01586193002942505,0.014404163879711298,0.013006050046663711,0.011701033764748243,0.010536273904069388,0.009575659625376832,0.008897549982047543,0.008579789361140643,0.008670568100530822,0.009163797066469519,0.010003855063921138,0.011114145246380255,0.012422630610508998,0.013872343252929046,0.0154215914812221,0.017040646814618275,0.018708282536079403],[0.06245484651171963,0.06153378116709839,0.06059751271210447,0.0596456363132385,0.05867773358454844,0.057693376535483,0.05669213237939258,0.05567356928858645,0.05463726318857863,0.053582805692725444,0.052509813289613134,0.05141793791020639,0.0503068790211027,0.049176397415717416,0.04802633090870334,0.046856612182691465,0.04566728909338764,0.044458547812717505,0.043230739284414205,0.041984409587442074,0.04072033495612572,0.03943956239883707,0.03814345709696995,0.03683375805930863,0.03551264385716983,0.034182810668182254,0.03284756528944255,0.031510936188554425,0.030177805925730175,0.028854068172622982,0.027546811656353695,0.02626453095062442,0.0250173589553758,0.023817306424268915,0.022678477798691817,0.02161720784430189,0.020652030251434878,0.019803353750657594,0.01909270180949889,0.018541402582212194,0.01816873599456698,0.017989763941638245,0.018013315975128,0.018240717917842902,0.018665691917506225,0.01927545452940197,0.020052623348207167,0.020977352802579063,0.02202920886828125,0.023188529852972435],[0.06666913490069401,0.06581590132742939,0.06494721722716545,0.06406280169131975,0.06316238796816653,0.06224572929795374,0.061312605561190114,0.060362830807893,0.05939626174073223,0.0584128072311531,0.05741243895492404,0.05639520324233975,0.05536123424872066,0.05431076856302416,0.05324416138638968,0.052161904428161404,0.05106464568400739,0.049953211278390204,0.04882862957042071,0.04769215773567151,0.046545311043067535,0.04538989503972764,0.04422804082896914,0.043062243565003586,0.041895404174217804,0.04073087412241278,0.03957250274641141,0.03842468621356563,0.037292416510683914,0.036181327935085605,0.035097737308031375,0.0340486725202722,0.03304188207384209,0.0320858161386604,0.03118956761816186,0.030362760400721042,0.029615372257043512,0.028957482866340874,0.02839894433091983,0.027948982821844257,0.02761575493252229,0.027405898208876248,0.02732412758282269,0.027372932794092367,0.027552422720906324,0.02786034122760023,0.028292250824402992,0.02884185328261643,0.029501397991205516,0.030262123169064237],[0.0704327520396093,0.06965016454549486,0.06885322366788366,0.06804182125407031,0.06721588288077146,0.06637537409761614,0.06552030730420803,0.06465074929484724,0.06376682950469932,0.0628687489905167,0.06195679017779759,0.06103132740427198,0.06009283828651077,0.05914191593181035,0.05817928201069921,0.057205800695630644,0.0562224934575835,0.055230554693000374,0.0542313681269537,0.05322652390240723,0.05221783621717104,0.051207361306327706,0.05019741548471008,0.04919059285721667,0.048189782170018416,0.04719818210914949,0.04621931415200825,0.045257031842075725,0.0443155250925827,0.04339931784319249,0.042513257117984066,0.04166249130017908,0.04085243530325112,0.04008872035115581,0.03937712636876348,0.03872349561788373,0.038133627270714336,0.03761315412445303,0.037167404584301254,0.03680125522445572,0.036518981401536164,0.03632411516078512,0.036219320618617636,0.03620629676354361,0.03628571600986443,0.036457203956972196,0.03671936203843143,0.03706983069846083,0.03750538709013669,0.03802206862614332],[0.07376485510398889,0.07305463041800832,0.07233192890860496,0.07159680678632402,0.0708493641459182,0.07008975054744415,0.06931817099828981,0.06853489233827585,0.0677402500258284,0.06693465531816904,0.06611860283232365,0.0652926784662786,0.06445756765053957,0.06361406388934093,0.06276307753743361,0.061905644742306816,0.06104293646238738,0.06017626744868525,0.05930710504997311,0.058437077669391047,0.057567982662919175,0.05670179342721483,0.055840665375906366,0.05498694045008233,0.05414314975160648,0.05331201382913895,0.05249644008971115,0.05169951675824636,0.050924502770220516,0.050174812967299205,0.04945399798274596,0.04876571826457027,0.04811371180219143,0.04750175530821394,0.04693361886882702,0.04641301441632154,0.045943538787986744,0.045528612597848225,0.04517141662825765,0.04487482790085268,0.04464135795464168,0.04447309608363213,0.044371660314816264,0.04433815870429711,0.044373163087142634,0.04447669676067592,0.04464823676972055,0.04488673057964252,0.0451906260648141,0.04555791299820778],[0.07666376146321471,0.07602465334706272,0.07537524253434764,0.07471571356868446,0.07404629728858801,0.07336727523255063,0.07267898423786424,0.07198182121605835,0.07127624808282423,0.07056279681456475,0.06984207459716418,0.06911476902511848,0.0683816533007154,0.06764359137341594,0.06690154294888656,0.06615656828521371,0.06540983268067432,0.06466261054307496,0.06391628891521686,0.06317237031470632,0.06243247472945936,0.0616983405933771,0.06097182455052576,0.06025489980174754,0.05954965281624295,0.05885827818390349,0.05818307138396511,0.05752641925409635,0.05689078796375165,0.056278708328974796,0.0556927583551509,0.055135542961334,0.05460967092575305,0.05411772919669184,0.05366225483421643,0.05324570498218362,0.0528704254102691,0.05253861830375588,0.052252310103895985,0.05201332030191157,0.05182323215314038,0.05168336629375781,0.05159475820313046,0.051558140356734415,0.05157392975969179,0.05164222134716476,0.05176278749832158,0.051935083652738925,0.05215825976149162,0.05243117706924272],[0.07911110897528537,0.078538341984269,0.07795740444714688,0.0773685675154072,0.07677214612273069,0.07616850214936004,0.07555804763454155,0.07494124801321603,0.07431862534907314,0.07369076153164499,0.07305830140029813,0.07242195575279026,0.0717825041905072,0.07114079774662295,0.07049776123728763,0.06985439526963186,0.06921177783400369,0.06857106540159162,0.06793349344264975,0.06730037627520682,0.06667310614974532,0.06605315147229836,0.06544205406720614,0.06484142538195627,0.0642529415407071,0.06367833716091267,0.06311939785957406,0.0625779513926622,0.06205585739370567,0.06155499570576857,0.061077253335174164,0.06062451009512884,0.060198623052225314,0.05980140993752159,0.05943463173482916,0.059099974709792384,0.05879903219159813,0.05853328646165728,0.05830409113709217,0.05811265445816317,0.0579600238950642,0.05784707247867504,0.05777448723073437,0.05774276002156015,0.0577521811192968,0.05780283561647347,0.057894602831329134,0.05802715868772141,0.05819998098376825,0.05841235737097004],[0.08107857210807329,0.08056409035475554,0.08004332811372973,0.07951660818666434,0.07898429239168993,0.07844678366966537,0.07790452815312954,0.07735801717500589,0.07680778919143987,0.07625443159034925,0.07569858235438616,0.07514093154408005,0.07458222256400547,0.07402325317195556,0.07346487618838292,0.07290799986088439,0.07235358783637137,0.07180265869191688,0.07125628497425433,0.07071559169770394,0.07018175425110333,0.06965599566633945,0.06913958320452429,0.06863382422095668,0.06814006127696315,0.06765966647570154,0.06719403501017686,0.06674457792513218,0.06631271411013324,0.0658998615589359,0.06550742794986658,0.06513680062305548,0.06478933605238345,0.0644663489322166,0.06416910102054359,0.0638987898999977,0.06365653783537677,0.06344338091955841,0.06326025870810768,0.06310800454545383,0.06298733678157771,0.06289885106727015,0.06284301389813363,0.06282015755293915,0.06283047654144258,0.06287402564143138,0.06295071956605283,0.06306033426203317,0.06320250979903055,0.06337675477185677],[0.08253418741226382,0.08206728399947037,0.08159565371787732,0.08111964755786964,0.08063965047154383,0.08015608268389099,0.07966940092371719,0.07918009955511765,0.07868871158877015,0.07819580955078614,0.0777020061853905,0.07720795496632729,0.07671435039065849,0.07622192802758143,0.07573146429410682,0.07524377592897113,0.07475971913608663,0.07428018836923644,0.07380611473069035,0.07333846395803488,0.07287823397587495,0.07242645199225287,0.07198417112373001,0.07155246653814545,0.0711324311101534,0.07072517059176134,0.07033179830822922,0.06995342939878117,0.06959117463152108,0.06924613383255945,0.06891938898043287,0.06861199702813706,0.0683249825261647,0.06805933013043981,0.06781597708854872,0.06759580580572769,0.06739963659822898,0.06722822074553428,0.0670822339540363,0.06696227034299326,0.06686883705858666,0.06680234961374361,0.06676312804011317,0.06675139392446286,0.06676726838518586,0.06681077102610766,0.06688181988499085,0.06698023237376445,0.06710572718729672,0.06725792713821171],[0.08344712766313166,0.08301515925398605,0.0825796520114512,0.08214097310247988,0.0816995195442626,0.08125571897152253,0.08081003030372118,0.08036294429675345,0.07991498396291077,0.07946670484217426,0.0790186951072903,0.07857157548461409,0.07812599897241018,0.07768265033821688,0.07724224537704895,0.07680552991267643,0.07637327852502022,0.07594629298789388,0.07552540040293905,0.07511145101769318,0.07470531571832799,0.0743078831907366,0.07392005674734564,0.0735427508212896,0.07317688713440156,0.07282339055080965,0.0724831846337336,0.07215718692926397,0.07184630400737571,0.07155142629703579,0.07127342275885029,0.07101313544507251,0.07077137400274393,0.07054891018105089,0.07034647240841048,0.07016474050813563,0.07000434062355115,0.0698658404239718,0.06974974466185373,0.06965649114862002,0.06958644721209477,0.06953990669221431,0.06951708752381487,0.06951812994601621,0.06954309536726815,0.06959196590380795,0.06966464459742948,0.06976095630646334,0.0698806492520827,0.07002339719085064],[0.08379086882444178,0.08337990339129117,0.08296622274824407,0.08255020733662753,0.08213226498585266,0.08171283134624216,0.08129237021039915,0.08087137371014677,0.08045036237570947,0.08002988504355077,0.07961051859915652,0.07919286754107747,0.07877756335274867,0.07836526366901185,0.07795665122491113,0.07755243257523728,0.07715333657449391,0.07676011260847256,0.07637352857047905,0.07599436857746818,0.07562343042393024,0.0752615227743376,0.07490946209829397,0.0745680693562205,0.07423816644742395,0.07392057243668461,0.07361609958000485,0.07332554917479808,0.07304970726447346,0.07278934023197119,0.07254519032119729,0.07231797112936066,0.07210836311677939,0.07191700918365282,0.07174451036544842,0.07159142169979581,0.07145824831800292,0.07134544181342349,0.0712533969368587,0.07118244866594757,0.07113286969112145,0.07110486835522994,0.07109858707750479,0.07111410128526399,0.07115141886885833,0.07121048016704072,0.07129115848143093,0.071393261110293,0.07151653088368119,0.0716606481743702],[0.08354519947190302,0.08314055529828486,0.082733661355828,0.08232491439283195,0.08191473814716023,0.08150358362049456,0.0810919292289774,0.08068028081782941,0.08026917152738659,0.07985916149798666,0.0794508374012643,0.07904481178571493,0.0786417222248786,0.07824223025720499,0.07784702010760987,0.07745679718194852,0.0770722863271287,0.07669422985139017,0.07632338530139611,0.07596052299522758,0.07560642331314348,0.07526187375105922,0.07492766574508447,0.07460459127912192,0.07429343929141041,0.07399499189994765,0.0737100204708743,0.07343928155805375,0.07318351274614608,0.07294342843333075,0.07271971559336869,0.07251302955977876,0.07232398987741236,0.07215317626852262,0.07200112476142816,0.0718683240299709,0.0717552119910939,0.0716621727059682,0.07158953362716984,0.07153756323046843,0.07150646906489934,0.07149639624904545,0.07150742643498649,0.07153957725434038,0.07159280225340796,0.07166699131684194,0.07176197157169892,0.07187750875640889,0.07201330903230777,0.07216902120909909],[0.08269762811711984,0.08228433372206113,0.08186889211510529,0.08145172184799902,0.08103327042144641,0.08061401457225942,0.08019446041939857,0.07977514345470336,0.0793566283639946,0.07893950866426813,0.0785244061429199,0.07811197008536926,0.07770287627811387,0.07729782577518055,0.07689754341716254,0.07650277609358039,0.076114290741195,0.07573287207315743,0.07535932003651363,0.07499444699859706,0.0746390746662398,0.07429403074548635,0.0739601453535862,0.0736382471994153,0.07332915955307637,0.07303369603017279,0.07275265622103967,0.07248682119994176,0.07223694895377258,0.07200376977398032,0.07178798165915126,0.07159024577874737,0.07141118205078212,0.07125136488758127,0.07111131916410449,0.07099151646250156,0.07089237164458476,0.07081423980069845,0.0707574136190732,0.07072212121423745,0.07070852444652875,0.07071671775735808,0.07074672753681628,0.07079851203170034,0.07087196179330833,0.07096690065566262,0.07108308722641453,0.07122021686479647,0.07137792411383195,0.07155578554776704],[0.0812446293419928,0.08080787655284244,0.08036869254396752,0.07992752179019362,0.0794848422819673,0.07904116603416583,0.07859703943109703,0.07815304338876397,0.07770979331508658,0.07726793884858647,0.07682816335608907,0.07639118317032137,0.07595774654893026,0.07552863233745966,0.07510464832025378,0.07468662924514238,0.07427543451015561,0.07387194550344611,0.07347706259109513,0.07309170175156034,0.07271679086019063,0.07235326563246684,0.07200206524039046,0.07166412762266673,0.07134038451592274,0.07103175624104387,0.07073914628564676,0.07046343573055631,0.07020547757471053,0.06996609101895225,0.06974605577444251,0.06954610646570437,0.06936692720134256,0.06920914638707208,0.06907333185564554,0.06895998638646639,0.06886954368403495,0.06880236487889659,0.06875873560750903,0.06873886371857,0.0687428776430607,0.06877082545385303,0.06882267462853774,0.06889831251653325,0.06899754749893496,0.0691201108173534,0.0692656590365552,0.06943377709539926,0.06962398189164165,0.06983572633888695],[0.07919294646842893,0.07871863303135844,0.07824117475545699,0.07776104017706237,0.07727873868098836,0.0767948215272496,0.07630988269300404,0.07582455950248865,0.07533953301653054,0.07485552815223757,0.07437331350276796,0.07389370082672528,0.07341754417679791,0.07294573863785081,0.07247921864587617,0.07201895586111061,0.07156595657133343,0.0711212586049589,0.07068592773811593,0.07026105358553497,0.06984774497178305,0.06944712478721499,0.06906032434192139,0.06868847724087493,0.06833271281427711,0.06799414914860157,0.06767388577575281,0.06737299608979314,0.06709251957244697,0.06683345391963334,0.06659674717112382,0.06638328995358218,0.0661939079532222,0.06602935473766908,0.06589030504694565,0.06577734867053961,0.0656909850210847,0.06563161850530427,0.06559955477967076,0.065594997962062,0.06561804885202649,0.06566870419172861,0.06574685697796802,0.06585229781364832,0.06598471726553076,0.06614370917484125,0.06632877484901735,0.06653932804719634,0.06677470065940982,0.06703414897016784],[0.0765608877242642,0.07603635690827427,0.07550748477301732,0.07497475029454749,0.07443868325826608,0.07389986623676802,0.07335893638201033,0.07281658699284684,0.07227356881599191,0.07173069103560174,0.07118882190398645,0.07064888896360876,0.07011187880860803,0.0695788363327896,0.06905086341050734,0.0685291169573581,0.06801480631932677,0.06750918994220735,0.06701357127803152,0.06652929389209955,0.06605773574325124,0.0656003026214142,0.06515842074033665,0.06473352849978427,0.06432706745025422,0.06394047251421071,0.06357516154057263,0.0632325242931082,0.0629139109977489,0.06262062059768568,0.062353888887358766,0.062114876715901914,0.061904658466004375,0.06172421102431025,0.0615744034633019,0.061455987651271006,0.06136958999593735,0.06131570450840105,0.061294687347732836,0.061306752973402635,0.06135197199414434,0.06143027075936891,0.06154143269473453,0.06168510133900394,0.06186078499687295,0.06206786288393583,0.062305592606952134,0.06257311879632937,0.06286948268901107,0.06319363244907315],[0.07337923297849518,0.07279431206172961,0.07220333030572551,0.07160674481742385,0.07100507524796708,0.07039890731193073,0.06978889617548643,0.06917576966237421,0.06856033122045348,0.06794346258515586,0.06732612606946381,0.06670936640320882,0.06609431203768902,0.06548217582508499,0.06487425497619896,0.06427193019503732,0.06367666388515945,0.06308999732108238,0.06251354667898266,0.06194899782519791,0.06139809976933441,0.060862656701926435,0.06034451855527466,0.059845570050956094,0.05936771822896068,0.058912878491611406,0.05848295924010139,0.058079845231862645,0.05770537984171652,0.05736134646685508,0.05704944937252544,0.05677129432864621,0.05652836943385789,0.056322026558904205,0.056153463862115956,0.05602370983296454,0.05593360930291897,0.055883811825139545,0.055874762766336315,0.05590669737746629,0.055979638018439276,0.05609339461056962,0.05624756828495253,0.05644155809145248,0.05667457053758536,0.05694563164450043,0.05725360114261862,0.05759718838483423,0.05797496953152563,0.05838540555837612],[0.06969103212602598,0.06903943439531053,0.06837955022141641,0.06771175702893381,0.06703650610113399,0.06635432831414623,0.06566583990180035,0.06497174819660702,0.06427285728244049,0.06357007348322607,0.06286441059922142,0.062156994788266605,0.06144906897366687,0.06074199664326447,0.0600372648859789,0.05933648649303387,0.05864140093186079,0.057953873982141954,0.057275895806832774,0.05660957721784186,0.055957143888305215,0.055320928263423504,0.05470335893232745,0.054106947247345966,0.05353427101734819,0.052987955161258544,0.05247064928849402,0.051985002275930996,0.051533634035357455,0.05111910480831236,0.05074388248118344,0.050410308573993146,0.05012056371028427,0.04987663350956294,0.04968027594348581,0.049532991248476016,0.04943599547921968,0.04939019871235398,0.04939618876638799,0.04945422109824038,0.04956421528137309,0.04972575818391686,0.049938113669761475,0.05020023836478679,0.050510802785865276,0.050868216939185175,0.05127065936776899,0.05171610856973009,0.05220237571593918,0.05272713765991175],[0.06554930140572728,0.06483036007923251,0.06410054511002494,0.06336006783586834,0.06260922022398814,0.06184838331433661,0.06107803600430344,0.060298764142242486,0.059511269886418666,0.05871638127257158,0.057915061916689665,0.05710842075913121,0.05629772173124081,0.05548439319535683,0.05467003697289925,0.0538564367324675,0.05304556546019752,0.05223959167801962,0.05144088401254923,0.05065201364960853,0.04987575413955342,0.049115077950988746,0.04837314911144632,0.047653311231830135,0.046959070198077296,0.04629407084198338,0.04566206698859995,0.045066884435307736,0.04451237666082055,0.04400237339894692,0.04354062264077035,0.04313072713575331,0.042776077016528705,0.04247978072581603,0.0422445969136928,0.042072870327346926,0.041966474863329675,0.04192676683973947,0.04195455114742849,0.042050062269344324,0.042212961271908864,0.042442348864458135,0.0427367936062563,0.043094373430917474,0.04351272795169029,0.04398911856990057,0.04452049325284169,0.04510355295640216,0.04573481699071775,0.046410685095737626],[0.06101160601329159,0.06023212240366111,0.05943918119561095,0.058632719998838186,0.0578127534127163,0.05697938401133981,0.05613281409100501,0.05527335820663035,0.054401456521860785,0.053517688993731945,0.05262279040576434,0.05171766625189213,0.05080340945595078,0.04988131788530269,0.04895291257972546,0.04801995656438719,0.047084474044314074,0.0461487696822315,0.045215447536443,0.04428742907475333,0.04336796947906332,0.04246067120969422,0.041569493508897166,0.04069875619609538,0.03985313576013413,0.03903765141797699,0.038257638536282154,0.037518706676661386,0.03682667962508631,0.036187515215582805,0.035607203672650946,0.035091644660317174,0.0346465052505947,0.034277063503152676,0.03398804501810327,0.033783462263449054,0.03366646816022817,0.03363923581323848,0.03370287505146699,0.03385739355322321,0.034101706128807675,0.034433690910401764,0.03485028661477558,0.03534762149176526,0.03592116256588155,0.036565873453002634,0.03727637016351044,0.03804706642695528,0.038872302655807385,0.03974645523327386],[0.056131117090142,0.05530682714580616,0.05446717222618863,0.05361171295336814,0.0527400674344976,0.05185192354575368,0.05094705231064334,0.0500253224678974,0.04908671634292508,0.04813134715863574,0.04715947794632099,0.04617154224492894,0.04516816680671321,0.04415019655749154,0.04311872208812765,0.04207510997627361,0.04102103624743946,0.03995852327215586,0.03888998034644728,0.037818248094236444,0.03674664663146767,0.03567902709954797,0.03461982565270943,0.03357411819767608,0.03254767305060092,0.031546997112058,0.030579369109760283,0.029652850942460736,0.028776265358942395,0.027959125577220845,0.027211500837047698,0.02654380258092179,0.02596648059928813,0.025489628538365,0.025122514101706808,0.024873069348577942,0.02474739603916233,0.024749352986807235,0.024880290021650948,0.025138973562983655,0.025521715742109305,0.02602268234215611,0.026634326038914444,0.02734787830983767,0.028153836948345796,0.029042401552973558,0.030003829436503805,0.031028702927276115,0.03210811256979608,0.03323376852017991],[0.05094538863178343,0.050101273483611874,0.049241568752654605,0.048365404205157975,0.04747193116629576,0.04656033424254386,0.045629844114317565,0.04467975148586766,0.04370942230974289,0.042718314442825575,0.04170599594238313,0.04067216527672065,0.03961667380974574,0.03853955102699245,0.03744103310875215,0.0363215956318962,0.035181991405659446,0.03402329472988729,0.03284695372034154,0.03165485278777541,0.030449387894961166,0.02923355784591963,0.02801107555311881,0.026786503890384946,0.025565421163307407,0.024354620988048414,0.02316234965182266,0.02199857939000578,0.020875306082333508,0.019806841172756565,0.018810036093276992,0.017904330874180044,0.01711146270839776,0.016454629629507698,0.015956932425038782,0.015639084431798882,0.015516708160446013,0.015597909669797466,0.015881959994916765,0.016359595741340608,0.017014799950557914,0.01782737193619825,0.018775475670887713,0.019837623624923237,0.02099392644731462,0.022226700204047475,0.0235206237594001,0.02486263229079175,0.026241684025417367,0.027648485824314565],[0.04546691937427197,0.044635549414167794,0.04379128033798477,0.04293285362490807,0.042058987788106496,0.041168389043026755,0.04025976276900956,0.03933182572017315,0.0383833189505455,0.03741302143407553,0.03641976438396147,0.03540244630983397,0.03436004889882391,0.03329165387191178,0.03219646105695039,0.031073808044544737,0.02992319196806623,0.02874429419850486,0.02753700910617087,0.02630147857420194,0.025038134749777768,0.023747754746279246,0.0224315329281049,0.02109117947074798,0.019729058875169347,0.01834839041011631,0.01695354653225372,0.01555050963786787,0.0141475899139232,0.012756580756530002,0.01139465125378593,0.010087453468602852,0.008874056011946825,0.00781383692738152,0.006992441807488926,0.00651534555858491,0.006471128309074864,0.006876692167597254,0.007666203040718084,0.008738734138832928,0.010004161950123259,0.011397420816737358,0.01287501367231871,0.014408196747192766,0.015977627712630074,0.017569893082396357,0.019175375164642416,0.02078695040823453,0.022399184600570107,0.024007824556272053],[0.0396825559144655,0.03890016716221704,0.03811170896676209,0.037315685878679526,0.036510537293165175,0.03569465013546656,0.03486637261837281,0.03402402890674376,0.03316593451591471,0.03229041226969964,0.03139580865001114,0.03048051038399678,0.02954296113639434,0.02858167820510586,0.027595269158032173,0.026582448401378328,0.025542053738205357,0.02447306306857102,0.02337461151213465,0.022246009423197374,0.021086762056074078,0.01989659209568519,0.018675467022840713,0.017423634579414354,0.016141671914746802,0.01483055831673874,0.013491789890964338,0.012127572032725761,0.0107411639999586,0.009337540966766185,0.007924774014320405,0.006517199384041035,0.005143584214923446,0.00387087438127746,0.0028753295968703663,0.0025482260404361963,0.003133034058664941,0.004284287641553085,0.005674205530794758,0.007168842517216133,0.00871563984825523,0.01029063959048767,0.01188106929998405,0.013479152111840925,0.015079622047860496,0.01667861152050581,0.018273105747832544,0.019860654036406276,0.021439206680289508,0.02300701729254072],[0.03356953433634167,0.03287060108906918,0.032177580767431435,0.03148894821763275,0.03080306742216988,0.030118211824859176,0.02943258745471278,0.028744358619859772,0.0280516759426637,0.02735270653841556,0.02664566620651142,0.025928853609159502,0.02520068656369183,0.0244597407779101,0.023704791624689185,0.022934859898927722,0.022149262951342993,0.021347673184683766,0.020530186677356708,0.01969740573168393,0.018850540508418955,0.017991536689960994,0.017123238368154495,0.016249598020437284,0.015375948144921853,0.014509350733675819,0.013659038476593829,0.01283694931664795,0.012058321957579346,0.011342245079662581,0.010711916388251757,0.01019417467044498,0.009817720141526654,0.009609606676002379,0.009590392875822428,0.00976959822416357,0.01014370247060327,0.010697772507368076,0.011409662404751929,0.012254617814474332,0.013208694540969597,0.01425059281294837,0.015362263991759089,0.01652881402770361,0.017738103469141602,0.018980273482581456,0.020247304091488772,0.021532641569940093,0.02283089914290311,0.024137622293101228],[0.027132123314234508,0.026544221638631363,0.025980292887439183,0.02543892780158096,0.024918497418066347,0.024417184380572717,0.023933021229222366,0.02346393485178285,0.023007796097925998,0.022562473467188034,0.02212588978373571,0.021696080860251536,0.021271255312397493,0.020849854890441756,0.0204306149159046,0.020012624615282727,0.01959538729293401,0.019178880339779377,0.018763614985403687,0.01835069541046351,0.017941876274528902,0.017539616801759778,0.017147128223646682,0.016768409550456893,0.0164082643538013,0.016072288674401667,0.01576681777809929,0.015498818113521969,0.015275711743699565,0.015105125238495633,0.01499456471899747,0.0149510333706016,0.014980624933600592,0.015088141470543824,0.015276789765933878,0.015548003273612283,0.015901415609539518,0.016334983089006185,0.016845227099461,0.017427550401923605,0.018076578098319064,0.01878648187635886,0.019551259984149166,0.020364959829645493,0.0212218416393828,0.02211648897905562,0.023043875472844352,0.023999397825366076,0.024978884392976096,0.025978586967623833],[0.020455291838503968,0.01999628471226471,0.019587040142308377,0.01922613959557072,0.018911565389817846,0.01864075029622657,0.018410653174310534,0.01821785610051819,0.018058676673824204,0.017929288283396527,0.01782584116382031,0.017744577910247354,0.01768193851498566,0.01763465160737401,0.017599810148670812,0.01757493115077213,0.017557999944517306,0.017547500097443203,0.01754243031059067,0.017542309581886874,0.01754717169595395,0.01755754977223635,0.01757445125402345,0.017599323420179083,0.01763400931092186,0.01768069393156384,0.01774184077428796,0.0178201190998977,0.01791832304289536,0.01803928440047761,0.018185781851132357,0.018360450191750536,0.018565693826918146,0.018803609034654355,0.019075919351776258,0.01938392772536083,0.019728487916137724,0.02010999616031647,0.02052840250879988,0.020983239795106343,0.021473667030409153,0.021998523308109353,0.022556388054761553,0.023145643641713076,0.023764536869967726,0.02441123653356093,0.02508388503330872,0.025780642756268988,0.026499724591810308,0.02723942848917756],[0.013765585809825683,0.01344488944039635,0.013212354699327258,0.013065408760414185,0.012999445291148385,0.013008085189668837,0.013083594775669697,0.013217388342034007,0.01340053575673615,0.013624211040114114,0.013880044341358025,0.014160366271069265,0.01445835297275446,0.014768090680755354,0.015084581373589962,0.015403709311278917,0.01572218430906424,0.016037473272555412,0.016347727700941523,0.016651711877689063,0.01694873431359391,0.017238583548695032,0.01752146848986282,0.017797962910229042,0.018068953450220197,0.018335590357637727,0.018599240232872787,0.018861440170900877,0.019123852890043137,0.01938822268872228,0.019656332354567905,0.019929961441081934,0.020210846597823427,0.020500644860683998,0.020800900950493115,0.021113019667281106,0.02143824439002857,0.021777642496336007,0.022132098216407305,0.022502313057710895,0.02288881351775404,0.023291965384947114,0.0237119935533775,0.02414900598207518,0.024603020238296164,0.02507399098996623,0.025561836854321906,0.026066465156226917,0.026587793380515465,0.02712576639268155],[0.007492766471784536,0.007321451002632227,0.007307281151574894,0.007438245292784844,0.007694308290012943,0.008051471110218925,0.008485649299145203,0.00897520088246955,0.009502006652381205,0.010051561890124544,0.010612578579445,0.011176432114447923,0.011736622111013619,0.01228831237212738,0.012827962408741058,0.013353041355564463,0.013861808939561333,0.014353148476681515,0.01482643937240911,0.01528145941812901,0.01571830961367549,0.01613735612586872,0.016539185339530367,0.016924568870369694,0.01729443600403098,0.017649851412663384,0.017991996274365648,0.018322151157447546,0.018641679285287864,0.018952009101806385,0.019254615424881223,0.01955099889894145,0.019842663915715035,0.020131095628015898,0.020417737091619162,0.02070396788801225,0.02099108576310017,0.02128029283107626,0.021572687722275507,0.021869264703373196,0.022170920294792052,0.022478467301552077,0.02279265552350921,0.02311419779023117,0.023443799443730574,0.023782189026836462,0.024130147765163715,0.024488535472289852,0.024858310752949964,0.0252405437986561],[0.0024214612907267523,0.002483821388639383,0.002873897035622493,0.003456910179150855,0.004130941670909484,0.004840769092580141,0.005558360769707516,0.006269155664396745,0.006965303915668882,0.0076424663459766975,0.008298244003329278,0.00893136681493146,0.009541252948112679,0.010127758270078188,0.010691027101883873,0.011231398278996618,0.011749341927361701,0.01224541388089382,0.012720221248535507,0.013174396460719927,0.013608579192443572,0.014023406410411752,0.014419510789926452,0.014797527202480568,0.015158106166424502,0.015501932321458883,0.015829745319128907,0.016142360137459493,0.016440683787022084,0.016725725683605922,0.016998599586065862,0.017260515877332027,0.01751276402524062,0.017756686207672397,0.017993644221742187,0.018224982807176444,0.01845199328162624,0.018675881796793498,0.018897746485251665,0.01911856722486797,0.01933921070525646,0.019560452014435466,0.01978301222074309,0.02000760960858928,0.020235020567272676,0.02046614484886269,0.02070206917298206,0.020944123053042316,0.021193921249161345,0.021453388332592808],[0.0018155107424616148,0.002015811638348247,0.002423910210160054,0.0029275082076158005,0.003465146695527577,0.004008164854030882,0.0045434786237909695,0.005065186686956446,0.005570786948928228,0.006059413118189493,0.006530980874637896,0.006985773655904351,0.007424252365600375,0.00784697730609004,0.008254577941580337,0.008647732343150728,0.00902713634013118,0.009393456458316702,0.009747271167196259,0.010089011325457926,0.010418912763046639,0.010736992134722817,0.011043052710373175,0.011336721199784487,0.011617511513642384,0.0118849075294427,0.012138454845492658,0.01237785105570623,0.012603024877258345,0.012814196071485475,0.01301191015850137,0.013197044218750145,0.013370782506810727,0.013534563156647717,0.013689999924884995,0.013838785635020882,0.013982586578533076,0.014122939296538097,0.014261162493661873,0.014398296865048388,0.014535083956908208,0.014671991651623275,0.014809288639909575,0.014947163912038238,0.015085880848143118,0.01522595007884624,0.015368301954327116,0.015514438795624247,0.015666549104995514,0.015827570049013424],[0.002432046900562667,0.0024553393650204236,0.0025735763767537716,0.002747709544701848,0.002948761544434647,0.0031590613637869818,0.0033694705051623038,0.0035761849883887272,0.0037782450736223924,0.0039758695760645614,0.00416950525840586,0.0043594481913051975,0.004545865146260247,0.004729017868902529,0.004909504239478403,0.005088381024410358,0.005267102446432403,0.005447278277616759,0.005630314139744455,0.005817034823084714,0.006007395590718593,0.006200352722406964,0.006393910223434437,0.006585312598369542,0.00677133011671075,0.00694858154372089,0.007113850244613591,0.007264364038857474,0.0073980218794402934,0.007513559225529994,0.007610648790120739,0.007689935153700571,0.007753001908881763,0.0078022699752836235,0.007840826879657365,0.007872190359347699,0.007900016461778183,0.007927772435378486,0.007958406947763537,0.007994061872897225,0.008035877293909468,0.008083940443341904,0.008137416590089552,0.008194873371983592,0.008254771937260446,0.008316058945319003,0.008378768750044513,0.008444543056343567,0.008516990180847646,0.008601827817808716],[0.0014909964715004822,0.0012235431318124899,0.0010785081494873506,0.001031545720006018,0.0010399702521909533,0.0010663653607354082,0.0010899438209617468,0.0011038579102467677,0.001109137030785944,0.001109512760451884,0.0011076281618372878,0.0011034501008389797,0.0010954432016280816,0.001082983445286344,0.0010688852896771099,0.0010613054149462898,0.0010739198258388264,0.001122732369160801,0.0012193684766869798,0.001365133768317063,0.0015513754935356475,0.0017645409759305506,0.0019904318209088487,0.002216142213818275,0.0024305732457080916,0.002624419039618928,0.0027900397142832274,0.0029213516473549127,0.0030137583177370975,0.0030641153718217436,0.0030707195877332063,0.003033314120144111,0.002953106111287355,0.002832796147152865,0.0026766219286039825,0.0024904204376617915,0.002281711560477107,0.0020597941630364556,0.0018358024818051287,0.0016225498143831775,0.0014337230294956477,0.0012816581763569277,0.0011732155172895374,0.0011054863298240155,0.0010663203928655493,0.0010417635798702107,0.001025704873431318,0.001027833030587243,0.001077033432907521,0.0012128898289640005]],[],[]]},{"xaxis.title":"C","xaxis2.title":"C","xaxis.range":[-9.0,1.0],"xaxis2.range":[-9.0,1.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"C","method":"update"},{"args":[{"x":[[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736]],"y":[[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1e-09,1.5998587196060573e-09,2.559547922699533e-09,4.094915062380419e-09,6.551285568595496e-09,1.0481131341546852e-08,1.67683293681101e-08,2.682695795279727e-08,4.291934260128778e-08,6.866488450042998e-08,1.0985411419875573e-07,1.757510624854793e-07,2.811768697974231e-07,4.498432668969444e-07,7.196856730011529e-07,1.151395399326448e-06,1.8420699693267164e-06,2.94705170255181e-06,4.71486636345739e-06,7.5431200633546225e-06,1.2067926406393289e-05,1.9306977288832496e-05,3.0888435964774846e-05,4.9417133613238384e-05,7.906043210907701e-05,0.00012648552168552957,0.00020235896477251554,0.00032374575428176466,0.0005179474679231213,0.0008286427728546842,0.001325711365590111,0.0021209508879201926,0.00339322177189533,0.005428675439323859,0.00868511373751352,0.01389495494373139,0.022229964825261957,0.03556480306223129,0.05689866029018305,0.09102981779915227,0.14563484775012445,0.2329951810515372,0.3727593720314938,0.5963623316594636,0.9540954763499964,1.5264179671752365,2.4420530945486547,3.906939937054621,6.250551925273976,10.0],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1.0554091871257525e-06,0.014529224019858405,0.07811032301764842,0.32809153963712656,10.0,1.6930771968603788e-09,3.8509551509170065e-06,6.25486376047316e-08,1e-09],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[1e-06,1.5264179671752333e-06,2.3299518105153717e-06,3.5564803062231285e-06,5.428675439323859e-06,8.286427728546843e-06,1.2648552168552958e-05,1.9306977288832496e-05,2.94705170255181e-05,4.498432668969444e-05,6.866488450042999e-05,0.00010481131341546864,0.0001599858719606059,0.0002442053094548652,0.00037275937203149417,0.0005689866029018299,0.000868511373751353,0.0013257113655901094,0.0020235896477251575,0.0030888435964774815,0.004714866363457394,0.0071968567300115215,0.010985411419875595,0.0167683293681101,0.025595479226995385,0.03906939937054621,0.05963623316594649,0.09102981779915227,0.13894954943731389,0.21209508879201924,0.32374575428176466,0.49417133613238384,0.7543120063354622,1.151395399326448,1.757510624854793,2.6826957952797272,4.094915062380427,6.250551925273976,9.540954763499943,14.563484775012444,22.229964825261955,33.9322177189533,51.794746792312125,79.06043210907701,120.67926406393313,184.20699693267164,281.17686979742365,429.1934260128778,655.1285568595523,1000.0],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736],[0.00012146074893687934,19.80297801403921,0.0008914845612019583,1000.0,1000.0,1000.0,1000.0,1000.0,344.7509371926736]],"z":[[[0.79348965166324,0.7873152101697144,0.780885756309152,0.7742744687750402,0.7675764461351676,0.7609103307914745,0.7544187173673151,0.7482665801784887,0.7426366755376367,0.7377205701810938,0.7337037942651832,0.7307443496353783,0.7289474710748803,0.7283471006331083,0.7289059467959619,0.7305318038037891,0.733097644601595,0.7364581484348216,0.740461955847344,0.7449610177045642,0.7498181557736581,0.7549132909762875,0.7601484000641402,0.7654511896099171,0.7707775619709192,0.7761130373955104,0.7814733225141631,0.7869041738245173,0.792480613580007,0.7983054322696919,0.8045067672262114,0.811234386244628,0.8186541336798615,0.826939826689315,0.8362617518593101,0.8467708743025475,0.8585780600860614,0.8717282367574971,0.8861707348399669,0.9017292020224981,0.9180770953781822,0.9347266465552104,0.9510388630339908,0.9662593849705435,0.9795819338752171,0.9902403828209791,0.9976330326180827,1.0014869470897054,1.0020287093983098,0.9999030808234651],[0.7931810251756211,0.7869631030094115,0.7804855935379387,0.7738216775047821,0.7670666535460815,0.7603396402406062,0.7537840821221494,0.7475662940776651,0.7418709913445163,0.7368924225078552,0.7328194964791169,0.7298138622794049,0.7279835232369231,0.7273630565638114,0.7279138301080764,0.7295414997202498,0.7321168294404261,0.7354923386270604,0.7395144801414337,0.7440329539067841,0.7489083226204692,0.7540183466874134,0.7592630466582752,0.7645684526441049,0.7698891120696688,0.7752095312945412,0.7805447564998041,0.7859402557958015,0.7914711698560708,0.797240871752136,0.8033786287785655,0.8100359946237402,0.8173813832220616,0.825592096583529,0.8348429263557018,0.8452903878808741,0.8570518051292103,0.8701790648756282,0.8846281896775795,0.9002281295692414,0.9166550007018852,0.9334201163727531,0.9498798286865315,0.9652721196674877,0.9787813700065514,0.9896318769043013,0.9972134456069592,1.001246954257477,1.0019554725134037,0.9999842413243117],[0.7928866152922683,0.7866270508127711,0.7801034684157527,0.7733890316921657,0.7665792068568742,0.759793539059954,0.7531762519997959,0.7468949060539388,0.7411360563185783,0.7360965005774196,0.7319684124582961,0.7289170457231668,0.7270532003763259,0.7264120965814371,0.7269537748751317,0.7285818473791955,0.73116501082566,0.7345537553810169,0.7385924382637657,0.7431285598381965,0.7480204452241661,0.7531436985527271,0.7583963797405675,0.7637028328716402,0.7690162358414085,0.774320060009308,0.7796286616227007,0.7849871808947451,0.7904708261909579,0.7961834906848207,0.80225549785317,0.8088401042255109,0.8161082055199663,0.8242405043693074,0.8334162303199426,0.8437974183416572,0.8555078802310212,0.8686065743466104,0.8830564167346919,0.8986919272314883,0.9151921632039545,0.9320677707488717,0.9486706751624281,0.9642314827670985,0.9779256776869397,0.9889686786914204,0.9967427939246212,1.0009638126179732,1.001850007018565,1.000044064866523],[0.7926067000898634,0.7863073864505195,0.7797397786324787,0.7729770053080411,0.7661146691690661,0.7592726934357739,0.752596010584911,0.746253330126408,0.740432923366489,0.7353339940434169,0.7311518477231854,0.7280552796300388,0.7261579055131685,0.7254955961101005,0.7260270894744489,0.7276540695408587,0.730243323633461,0.7336434520443048,0.7376968116826096,0.7422487553706665,0.7471553921242202,0.7522901744390531,0.7575491981994159,0.7628551133545809,0.7681597152653271,0.7734454207004782,0.7787258678289429,0.7840458305465208,0.7894805349401943,0.7951343320905149,0.8011385274622489,0.8076479959270382,0.814836024289952,0.8228866267815068,0.831983396721241,0.8422938492151177,0.8539483042361581,0.8670128963524733,0.8814576337710401,0.897122877144947,0.9136909145550192,0.9306719826018124,0.9474138131051497,0.96313992674296,0.977017371678066,0.9882534134008278,0.9962238901197426,1.0006404476482738,1.0017152419046425,1.0000853290517429],[0.7923415445963937,0.7860044274619257,0.7793949039693798,0.7725860515652336,0.7656735797751018,0.7587777426472408,0.7520441117055293,0.7456424484708427,0.7397626130157059,0.7346060620482994,0.7303710813640804,0.727229920912652,0.7252990199203676,0.7246149073665383,0.7251350577543169,0.7267593650269726,0.7293528809602715,0.7327624630472311,0.7368285658416679,0.7413944468966253,0.7463140204680626,0.7514585925274331,0.7567222927244128,0.7620260703968461,0.7673203271109962,0.7725864071125884,0.7778372038225004,0.7831170876406441,0.7885012533463065,0.7940944482443215,0.8000288854517651,0.8064609725498224,0.8135662941592879,0.8215320825712662,0.8305462139327758,0.8407816349839149,0.8523751841710443,0.8654002683987323,0.8798341832148555,0.8955234044757483,0.912153748251687,0.9292353065033295,0.9461118562184561,0.9620001307999,0.9760592199957487,0.9874889873682002,0.9956598376602402,1.0002800158181013,1.0015542387452814,1.0001108661181526],[0.792091400196117,0.7857184752876802,0.7790692053064188,0.7722166016289759,0.7652564524768478,0.7583092968677506,0.7515212765578119,0.7450631076848799,0.739126108672709,0.7339138275383214,0.7296273599081092,0.7264422976449804,0.7244778970465452,0.7237713533731732,0.7242789337105728,0.7258989043885338,0.7284947707192244,0.7319118012262513,0.7359886480029167,0.7405665255195651,0.745497174423966,0.7506497598649418,0.75591644444197,0.761216472222514,0.766498841622038,0.7717438082242409,0.7769634956395721,0.7822018349835675,0.7875339418215416,0.7930648987388659,0.7989277523063937,0.8052803563738501,0.8123004978804164,0.8201785294443896,0.8291065224580436,0.8392627976930485,0.8507907118257766,0.8637710308766556,0.8781885285612854,0.8938960733433559,0.9105833146096604,0.9277604721045157,0.9447676121538,0.9608149875729052,0.9750542230661189,0.9866785513594398,0.9950539588282473,0.9998858195652975,1.001370116640682,1.0001234929502005],[0.79185650406231,0.7854498145370845,0.7787630236714616,0.7718690633774352,0.7648637739617568,0.7578679350275607,0.7510281908843,0.7445161150707651,0.7385243518037766,0.7332583713177933,0.7289218907322724,0.725693702477975,0.7236958559394147,0.7229662215523153,0.7234599359499816,0.7250738255119336,0.7276700522428956,0.7310924551733382,0.735177985113,0.739765865257829,0.7447056835964421,0.7498644709109337,0.7551324235402441,0.7604270776400042,0.7656960211823916,0.7709184068763297,0.7761055651939162,0.7813009537115708,0.7865795621752739,0.792046748472099,0.7978363188467634,0.8041074865033933,0.8110401433446595,0.8188276607349831,0.8276662113189082,0.8377394231444498,0.8491971598472242,0.8621276230671772,0.87652325013244,0.8922435819885465,0.908982414822255,0.9262503763528046,0.9433840717706351,0.9595875875511277,0.9740055895816815,0.9858254594611539,0.9944097256526846,0.9994612245290254,1.0011659686429775,1.000125933431746],[0.7916370786204158,0.7851987122932951,0.7784766793368024,0.7715438202203391,0.7644960022486547,0.7574542027558647,0.7505655022331053,0.7440022349761225,0.7379582370915604,0.7326407258882839,0.7282558350163431,0.7249853855285648,0.7229541741396673,0.722200756911256,0.7226792419896644,0.7242852292101933,0.7268797529250368,0.7303053866318319,0.734397481705497,0.7389933212688745,0.743940361448495,0.7491035060807796,0.7543709878860314,0.7596586346948387,0.7649126189680663,0.7701109783814646,0.7752642287966676,0.7804153216678505,0.7856390757904499,0.7910410655624782,0.7967557838239546,0.8029437160893075,0.8097867603991323,0.8174812018158533,0.8262272141031032,0.8362136566692596,0.8475968773324076,0.860472578575304,0.8748410401931316,0.8905687571915674,0.9073539941091004,0.9247080745630146,0.941964396915812,0.9583212015794617,0.9729167099964215,0.9849332263933083,0.9937306974657261,0.9990095841774969,1.000944774993773,1.0001207339880962],[0.7914333310440931,0.7849654174602225,0.7782104709682618,0.7712412299835063,0.7641535652149687,0.7570686104205114,0.750133817326474,0.7435221852368088,0.7374286076307074,0.732061869138521,0.7276303002423707,0.7243185467103723,0.7222540800147315,0.7214761548465326,0.7219379824587122,0.7235341748531736,0.7261248649361121,0.7295515279596685,0.7336480178511184,0.7382497281008142,0.7432020037347853,0.7483676302900146,0.7536328816362929,0.7589118793137583,0.7641493775874145,0.7693222891179431,0.7744402956543788,0.7795458117480232,0.7847134417538218,0.7900489191968464,0.7956873514170284,0.8017904094136857,0.8085418974720142,0.8161409062488325,0.8247915046706806,0.8346876984723063,0.8459922849123158,0.858808520184703,0.8731446974178358,0.8888745479486716,0.9057011339856861,0.9231367704161316,0.9405119068879253,0.9570192618235333,0.9717911286205525,0.9840054856070168,0.9930204663960945,0.9985341747887078,1.000709319840368,1.0001101729873882],[0.7912454527865308,0.7847501601544982,0.7779646748318748,0.7709616238667907,0.7638368592168882,0.7567116312833873,0.7497336995676148,0.7430766337686456,0.7369362502353775,0.7315227179748204,0.7270463322695835,0.7236943274730441,0.7215967445022826,0.7207935536234872,0.7212372352869296,0.7228216760970159,0.7254063420488654,0.728831779680727,0.7329304471673314,0.7375358979775013,0.7424913869493989,0.7476575915016633,0.7529188338469622,0.7581875339430487,0.7634070277130831,0.7685530951117916,0.7736345663492477,0.7786932902185402,0.7838036149451363,0.7890713774169048,0.7946322286401672,0.8006489388438326,0.807307118012798,0.8148085516799753,0.8233610925208301,0.8331637985450351,0.8443858693174687,0.8571381541228437,0.8714371207054721,0.8871640184176216,0.9040270436889271,0.9215398049670582,0.9390300637636091,0.9556853415919414,0.9706325152116888,0.9830459498901734,0.9922826113799568,0.9980381429725249,1.0004621197474988,1.0000961646480107],[0.7910736191492359,0.7845531511457073,0.7777395440628841,0.7707053054825471,0.7635462478134444,0.7563836997889462,0.7493656667145091,0.7426661953564659,0.7364818909398939,0.7310241220092086,0.7265049070501118,0.7231138019157332,0.7209832722367263,0.7201540266275459,0.7205780199852958,0.7221486967781163,0.7247250966105896,0.7281470081443406,0.7322455948980839,0.7368526191227487,0.7418092667914936,0.7469741192793219,0.7522295570816755,0.7574863061840205,0.7626862867089425,0.7678041406105698,0.7728478313057023,0.7778586150128097,0.7829105440908374,0.7881095048507445,0.7935916226668199,0.7995206816636578,0.806083996755668,0.813485935486513,0.8219380178226678,0.8316442511451069,0.8427801774178265,0.8554642637276758,0.8697213023392647,0.8854403401443356,0.9023350507968582,0.9199206447467159,0.9375224567654988,0.9543231343944202,0.9694446368336607,0.9820583755857373,0.9915206608992834,0.9975244673231681,1.0002053733182588,1.0000801622465836],[0.7909179888903229,0.7843745813478369,0.7775353080014046,0.7704725499812308,0.763282060604811,0.7560852100024886,0.7490301887485415,0.7422914286891704,0.7360661907799625,0.7305668574510331,0.7260069221095791,0.7225779672393496,0.720414692042657,0.7195585745389785,0.7199612921413051,0.7215161470399101,0.7240819966980478,0.7274980433117382,0.7315942560731554,0.7362006541284475,0.7411563766516203,0.7463179233483935,0.7515657460230621,0.7568088874286717,0.7619878572554234,0.7670761566527946,0.7720808692477256,0.7770426340100816,0.7820351697882295,0.7871643603964558,0.7925667380790472,0.7984070167917533,0.8048741158157684,0.8121748701845258,0.8205243461159776,0.830131388843145,0.8411778097311208,0.85378970250729,0.8680003204891733,0.8837067835836534,0.9006285910819155,0.918282869044566,0.9359927858464338,0.9529364325803544,0.9682313305933479,0.9810465310103488,0.9907380643376719,0.9969959349896464,0.9999409395482783,1.000063119398147],[0.7907787038741421,0.7842146213646043,0.7773521715987138,0.7702636032701476,0.7630445921942584,0.7558165142135534,0.7487276859641783,0.7419528336881318,0.7356897419448184,0.7301516213743102,0.7255531880050131,0.7220877335030448,0.719891946810478,0.7190081176530834,0.7193879382672342,0.720924879761008,0.7234778634890008,0.7268856766862968,0.7309771937552355,0.7355807383703805,0.7405334261209848,0.7456896921676812,0.7509280760892325,0.7561559514986587,0.7613124259768254,0.7663698596369999,0.7713344456514868,0.7762461833024163,0.7811784225064061,0.7862369948653718,0.7915587740510758,0.7973093213965966,0.8036790606297943,0.8108771786085247,0.8191221626905492,0.828627576139705,0.8395814133954129,0.852117386584419,0.8662773310541235,0.8819667089271096,0.8989111976370288,0.916630156455184,0.9344448446524654,0.9515291058539659,0.9669964776931643,0.9800141692578963,0.9899381715178794,0.9964551329327516,0.9996703472650079,1.0000455564572428],[0.7906558887638677,0.7840734210910294,0.7771903148976762,0.770078681330694,0.7628341012821678,0.7555779217182089,0.7484585273035493,0.7416508491731715,0.7353530643893242,0.7297790265523196,0.7251444200934529,0.7216439126594698,0.7194158828576477,0.7185034886462658,0.7188587711473096,0.7203756873501751,0.7229134688809034,0.7263106594019996,0.7303951373811101,0.7349935784744528,0.739941099525375,0.7450900915133571,0.7503172020581264,0.755528153290805,0.7606606620742937,0.7656859498945945,0.7706093111980394,0.775470085455298,0.7803412205706048,0.7853284485930263,0.7905689214768485,0.7962289674205013,0.8025004157540526,0.809594688876485,0.8177335666556699,0.8271352026585188,0.8379936746037608,0.850450286518074,0.8645555588406237,0.8802235562496994,0.8971864893120081,0.9149662707671009,0.9328825030099458,0.950105079906188,0.9657439790702301,0.9789650052697842,0.9891242196634187,0.9959044525397739,0.999394831568853,1.000027652952865],[0.7905496507584443,0.783951109373276,0.7770498925903051,0.7699179696386675,0.7626508098993177,0.7553696977921314,0.7482230289567154,0.7413858509054081,0.73505660298868,0.7294495970570171,0.7247812310839771,0.7212472068986321,0.7189872391190995,0.7180454261584603,0.718374525827429,0.7198692989669022,0.7223895333825973,0.7257737004814355,0.7298487812013688,0.7344398508348678,0.7393800544849025,0.7445197630771762,0.7497337567024218,0.7549261274324952,0.7600332159682981,0.7650251102708259,0.7699062002309909,0.7747151477676637,0.7795244681369602,0.7844397490263958,0.7895983600521256,0.795167318025111,0.8013397605348969,0.8083292291563656,0.8163606647145227,0.825656675925478,0.8364173105013628,0.8487914184950897,0.8628382880732215,0.8784808349859029,0.8954581584945706,0.9132950462643793,0.9313096890607623,0.9486683153440034,0.9644777327447063,0.9779026968326692,0.9882993267373409,0.9953461052793671,0.9991153893062035,1.0000093383809316],[0.7904600793750481,0.7838477937284385,0.7769310336549397,0.7697816226914012,0.7624949027853449,0.7551920628641843,0.7480214532446482,0.7411581500396153,0.7348007253067012,0.7291637648081227,0.7244641249587869,0.7208981966723601,0.7186066370729068,0.7176345695958314,0.717935856375963,0.7194063782158363,0.7219067242987761,0.725275465271096,0.7293387828208391,0.7339202001845296,0.7388509205001648,0.743979323080668,0.7491783494377766,0.7543504869504232,0.7594307179545715,0.7643880047182856,0.769225829224215,0.773982160537322,0.7787290531649249,0.7835719082964514,0.7886482553224213,0.7941257239723859,0.8001986646682174,0.8070826222527496,0.815005564661718,0.8241944137467345,0.8348550605486265,0.8471438348850762,0.8611288522307864,0.8767421127427021,0.8937299582659276,0.9116203725016057,0.9297303711465793,0.9472227870404549,0.9632016128760628,0.9768308290104905,0.9874664898849147,0.9947821463543092,0.9988328452438264,0.9999903815281727],[0.7903872462779746,0.7837635601255799,0.7768338410749447,0.7696697636445962,0.7623665269168568,0.7550451918978055,0.7478540077976807,0.7409679920105663,0.7345857200318688,0.7289218672221348,0.7241934928599578,0.7205973303779589,0.7182745731944908,0.7172714555233157,0.7175433335153636,0.7189875213493915,0.7214656542198532,0.7248165740577207,0.7288657618395812,0.7334352382166497,0.7383542975649073,0.7434693609069754,0.7486515649872774,0.7538018219563098,0.7588537768776025,0.7637752769075096,0.7685688952647929,0.7732718953379051,0.7779558453948833,0.7827259207854709,0.7877197557087408,0.7931055199561416,0.7990786836664272,0.8058566800349158,0.8136703686259366,0.8227508362037433,0.8333096773573564,0.8455106141533231,0.8594306232007978,0.8750110034541108,0.892005688955418,0.9099461786018569,0.9281485395190947,0.945772463976329,0.9619194504301005,0.9757529014206845,0.9866285875674463,0.9942145029310011,0.9985479218898455,0.9999704789838633],[0.7903312051546034,0.7836984728289409,0.7767583916402635,0.7695824840608055,0.762265791188161,0.754929213984933,0.7477208450374748,0.740815555868513,0.7344117961144739,0.7287241460562849,0.7239696113802943,0.7203449204722256,0.717991416087732,0.7169565158973872,0.7171974431834127,0.7186132559961866,0.7210668798218669,0.7243976008651115,0.7284302985917623,0.7329855422552416,0.7378907548048175,0.7429904377519896,0.7481539620651086,0.7532806983533531,0.7583029788259013,0.7631875488593326,0.767936074556479,0.7725851033136316,0.7772056943387045,0.7819027606989208,0.7868139895237222,0.7921080209002671,0.7979813542531404,0.8046531977304154,0.8123571660836728,0.8213283572881106,0.8317839170118646,0.8438948501278448,0.8577469997417677,0.8732911548778313,0.8902891841122584,0.9082764171151786,0.9265681879304303,0.9443212896003025,0.960635015291606,0.9746723177174854,0.9857883839352801,0.9936450035035047,0.9982613068194836,0.9999493434291311],[0.7902919916388355,0.7836525743038548,0.7767047358325485,0.7695198437705784,0.7621927662460379,0.7548442121545241,0.7476220619656205,0.7407009540689244,0.7342790826147287,0.728570747473049,0.7237926433780757,0.7201411482647939,0.7177574090262736,0.7166900782012287,0.7168985860340611,0.7182840404145704,0.7207109009725465,0.7240190724262986,0.7280329329771591,0.7325716539709335,0.7374608291417192,0.7425430852965076,0.747686072082643,0.7527876565673455,0.7577788858533756,0.7626254196037474,0.7673280209490693,0.7719225134982708,0.7764794272911641,0.7811033796520539,0.7859320619913461,0.7911345182407346,0.7969081897074233,0.8034739481109915,0.8110680266743113,0.8199293762047802,0.8302805288924484,0.8422996406192077,0.8560813952418068,0.8715862354301694,0.8885842959054442,0.9066150474627225,0.9249932951370669,0.9428731626998993,0.9593519996162047,0.9735923766421687,0.9849485340499035,0.993075405256856,0.9979737114002415,0.9999267922254638],[0.7902696232821301,0.7836258851855076,0.776672897793998,0.769481870846317,0.7621474844784072,0.7547902233950173,0.7475577002569754,0.7406242327114108,0.7341876292476213,0.7284617232777548,0.7236626410688263,0.7199860732017944,0.7175726764312041,0.7164723673370015,0.7166470778368943,0.7180002632516772,0.7203981601310102,0.7236814673213516,0.7276741633774606,0.732194078137375,0.7370650239822147,0.7421278044012934,0.7472483978803809,0.7523232103065738,0.7572820347312773,0.7620894638700858,0.7667453644991088,0.7712848311647772,0.7757778473702944,0.7803287042816134,0.7850750522838725,0.7901862762094163,0.795860675181105,0.8023206756004412,0.8098049928512063,0.8185562683783756,0.8288022450255071,0.84072807539542,0.854437224759266,0.8698999203503536,0.886894879955212,0.9049660189794011,0.9234278063332443,0.9414319187517365,0.9580740021976384,0.972516264035113,0.984111588717077,0.9925074168756296,0.9976859149485044,0.9999028303613954],[0.7902640995720084,0.7836184043102852,0.7766628753794205,0.7694685616879609,0.7621299401551942,0.7547672388874256,0.7475277466509661,0.7405853722129199,0.7341374075875816,0.7283970332166474,0.7235795508800983,0.7198796427544221,0.7174372321067104,0.7163035089633125,0.7164431506878087,0.7177622437705243,0.7201290420201492,0.7233852152666103,0.7273544456470471,0.7318532814225187,0.7367038079297543,0.7417450638272038,0.7468414124894434,0.7518878453547972,0.7568129357352765,0.7615802308133943,0.7661887100674016,0.7706727362120964,0.7751017315948175,0.7795796338932399,0.7842440105900697,0.7892645281385244,0.7948402630141312,0.8011950903367068,0.8085700724080016,0.8172113762044484,0.8273517689928005,0.839183223519374,0.852817891329686,0.8682358771799586,0.8852247795915348,0.9033332535561398,0.921875614516439,0.9400013117067058,0.9568045136304264,0.9714470452705262,0.9832799979142363,0.9919427150205616,0.9973987901441381,0.9998776809693405],[0.7902754019976309,0.7836301088090746,0.7766746402904683,0.7694798812186802,0.762140089718211,0.7547752044432088,0.7475321336294914,0.7405842883913374,0.7341283128765355,0.7283765481747784,0.723543219464408,0.7198217017718641,0.7173509877776312,0.7161835338789726,0.7162869549068864,0.7175702324918176,0.7199038735429565,0.7231306965367941,0.7270741921655651,0.7315496912082808,0.7363776135192571,0.7413952989829171,0.7464655579266516,0.7514820184018118,0.7563720714723221,0.7610982427819085,0.76565863595879,0.7700868815956501,0.7744518290068468,0.7788570381552989,0.7834399552291061,0.7883704728051425,0.7938483680742839,0.8000988622230576,0.8073652309240467,0.8158969995948684,0.8259317644421256,0.8376681200636455,0.8512267715222456,0.8665977505373842,0.8835778095269388,0.9017206278719283,0.9203405417791616,0.9385849961634375,0.9555469020689145,0.9703876576640692,0.9824561120592715,0.9913829535584262,0.9971133092852027,0.9998517563713161],[0.7903034941618035,0.7836609542614985,0.7767081382904042,0.7695157631878905,0.7621778522154448,0.7548140211387124,0.7475707403659315,0.7406208339279464,0.7341601663639642,0.7284000540867905,0.7235534003241302,0.7198120011295037,0.7173137612791907,0.7161123830489892,0.7161785614759715,0.7174244121843003,0.7197229239071499,0.7229182414974777,0.7268337709375139,0.7312836944316203,0.7360868359737968,0.7410789107033282,0.74612124402759,0.751106155916293,0.7559598957520216,0.7606439941305312,0.7651556926096351,0.7695278918079653,0.7738288588480275,0.7781617548498989,0.7826638698246837,0.7875052708358559,0.7928863631487411,0.7990336150055779,0.8061923841773274,0.8146153863745912,0.8245448432531324,0.8361857522275172,0.8496672002291453,0.8649891461612451,0.881957738922681,0.9001319551962359,0.9188263205186066,0.9371865098912606,0.9543043994186738,0.9693409025082182,0.981642180645431,0.9908297654475842,0.9968305347829776,0.9998256205805139],[0.7903483219385196,0.7837108749097115,0.7767632894972348,0.7695761105780615,0.7622431098738452,0.7548835461358407,0.7476433939262108,0.7406948001711345,0.7342327180978712,0.7284672563685723,0.7236097606327356,0.7198502056792169,0.717325284172762,0.7160899129207294,0.7161179648587255,0.7173248991282379,0.7195864049166961,0.7227481302218648,0.7266335047222579,0.7310556364399772,0.7358318319835178,0.7407962640623098,0.7458088473224573,0.750760653065816,0.7555768325073337,0.7602179500852035,0.7646804013283747,0.7689963614158384,0.7732335087972148,0.7774945876918412,0.7819167005540758,0.7866700411918311,0.7919555744158877,0.7980009204163041,0.8050533905777348,0.813368722595345,0.8231935534251702,0.8347390448945349,0.848142454673609,0.8634136141903106,0.8803682738190419,0.89857096673443,0.917336574559449,0.9358092566808245,0.9530800878413498,0.9683094365021248,0.9808403480322418,0.9902847578362434,0.9965515990282917,0.9997999531408599],[0.7904098136749134,0.7837797839300387,0.77683998875253,0.7696607961110359,0.7623357088035305,0.7549835936767938,0.7477498706999854,0.7408059192394225,0.7343456500811114,0.7285777846895404,0.7237118879730254,0.719935901537789,0.7173852087302869,0.7161159007556784,0.7161050860484472,0.717271744571127,0.7194944713843793,0.7226205921627566,0.7264736701765182,0.7308658198544115,0.7356129185079241,0.7405476872243135,0.7455287099599475,0.7504458726891315,0.755223274769401,0.7598205456630076,0.7642332530944296,0.7684928536602929,0.7726664332776537,0.77685630422613,0.7811993534867065,0.7858658577548754,0.7910572770264553,0.7970022924231206,0.8039500436775711,0.8121591228402568,0.8218803667689377,0.8333308456866223,0.84665573762762,0.8618746316412749,0.8788130388922892,0.8970412924831513,0.9158748001961863,0.9344564895255945,0.9518768865058117,0.9672957624547104,0.9800526464146655,0.9897495013541717,0.996277678254014,0.9997755142987039],[0.7904878804362774,0.7838675737604233,0.7769381060627863,0.7697696628488848,0.7624554598253026,0.7551139362391867,0.7478898980378594,0.7409538663793774,0.7344985797078718,0.7287311979280234,0.7238592968227529,0.7200686027549393,0.7174931142919174,0.7161900497810665,0.7161397757008413,0.7172649362927905,0.7194472216164335,0.7225358058481351,0.7263544969905726,0.7307145034347351,0.7354303716039728,0.7403334703401707,0.7452811386848505,0.7501621443259496,0.7548995837013593,0.7594521846527569,0.7638147074206045,0.7680178991254316,0.7721282518414391,0.7762476338144761,0.780512692026736,0.7850937460349924,0.7901926908234513,0.7960391816288833,0.8028840648198002,0.8109886206017312,0.8206076665000333,0.8319639095934398,0.845210159840851,0.8603755840393528,0.8772955584927459,0.895546441560096,0.9144443471808982,0.9331312941692671,0.9506975385737015,0.9663022192459991,0.9792809861797082,0.9892255147674849,0.9960099635672371,0.9997531114307511],[0.7905824162925909,0.7839741164813502,0.7770574871097731,0.769902524883725,0.7626021394125126,0.7552743058366838,0.7480631560691169,0.7411382625331562,0.7346910633993201,0.7289269891801109,0.7240514346950816,0.7202477574034594,0.7176485130246397,0.7163119940332746,0.7162218172269834,0.7173044001982224,0.719444697918448,0.7224938985669023,0.726276166999259,0.7306019009425935,0.7352844252840463,0.7401538644934376,0.7450664038755218,0.7499097633096146,0.7546060876959341,0.7591132386607208,0.7634251912839584,0.7675719944820736,0.7716195476387796,0.7756692657209415,0.7798575344738299,0.7843546800197103,0.7893629762303827,0.7951129698630999,0.8018570959875071,0.8098591588227476,0.8193777348499531,0.830640883284054,0.8438087216999526,0.8589197461506788,0.8758192369103989,0.8940897819748244,0.9130483997114938,0.9318365730912749,0.949544598463032,0.9653309711276994,0.9785271439974724,0.9887142461674756,0.9957496309943301,0.9997335666494218],[0.7906932986448155,0.7840992642476545,0.7771979538259255,0.7700591681104072,0.7627754907376236,0.7554643954494482,0.7482692796737447,0.7413586770711281,0.734922600364516,0.7291645907208831,0.724287687891304,0.7204727531339787,0.7178508551190927,0.7164813028177242,0.7163509297430763,0.7173900018602657,0.719486887071141,0.7224949460100415,0.7262388132496362,0.7305281800008793,0.7351752704098447,0.7400090807046855,0.744884738647793,0.7496889899281658,0.7543430815415714,0.7588040462259777,0.7630650981299185,0.7671556013118058,0.7711408659792887,0.7751218473064982,0.7792346517158562,0.7836495791850232,0.7885692303369821,0.7942249650098172,0.800870692920166,0.8087725806986613,0.8181927408279412,0.8293642892423713,0.8424542941660164,0.8575102617602086,0.8743873378065672,0.892674519816737,0.9116899575156848,0.9305750300432303,0.9484204194868089,0.9643839965271778,0.9777927490850616,0.988217051748071,0.9954978115029116,0.999717685504975],[0.7908203885890432,0.7842428497683819,0.7773593050305363,0.7702393510755736,0.7629752248133105,0.7556838605682044,0.7485078605824764,0.7416146306469905,0.7351926364215479,0.7294433788432914,0.7245673868541141,0.7207429222366537,0.7180995334662935,0.7166974847491799,0.7165267707961152,0.7175215479398553,0.71957372072503,0.7225389718318243,0.7262425190090576,0.7304934609511962,0.7351030536305085,0.7398992890022216,0.7447363380322984,0.7495000486593248,0.7541108256617453,0.7585249120097113,0.7627347869541687,0.7667691450167948,0.7706927129921471,0.7746059823418199,0.7786447650666766,0.7829793056871043,0.7878124832109648,0.7933763961150252,0.7999263185634262,0.8077306208421902,0.8170547282845101,0.828136509907999,0.8411495990824177,0.8561501224352214,0.8730029627423611,0.8913036778579224,0.9103718171782705,0.9293491552912813,0.9473271420122528,0.9634630765878794,0.9770792681347726,0.9877351730581948,0.9952555614675698,0.9997062267026076],[0.7909635313164268,0.7844046868316699,0.7775413171222305,0.7704428058962557,0.7632010217176022,0.7559323208355349,0.7487784495791338,0.7419055981357384,0.7355005678235798,0.7297626785226027,0.7248898111282384,0.7210575462517388,0.7183938878585935,0.7169599913650487,0.7167489388070378,0.7176987874185483,0.7197050756643146,0.7226259470956721,0.7262873167008093,0.7304978157153713,0.7350678763758004,0.7398246175687951,0.744621358232509,0.7493431274849462,0.7539095454319358,0.7582761060625338,0.7624345814665737,0.7664130138203563,0.7702755543915716,0.7741222294470755,0.778088544261502,0.7823446617530536,0.7870936944632807,0.7925684088158952,0.7990253369190886,0.8067348969179973,0.8159656044431501,0.8269597720490709,0.8398971890116016,0.8548421452147057,0.8716690287268801,0.8899800736101584,0.9090965539242573,0.9281612117604364,0.9462666823281344,0.9625697837336783,0.9763879894228755,0.9872697134434808,0.9950238337851992,0.9996998727522063],[0.7911225565466934,0.7845845708714456,0.7777437448230005,0.770669239240957,0.7634525318923948,0.7562093617681481,0.7490805587805813,0.7422310116184838,0.7358457450443077,0.7301217678728402,0.7252541939460208,0.7214158601706019,0.7187332087610507,0.717268220325367,0.7170169751948909,0.7179214125860638,0.7198807738922219,0.7227557895700193,0.7263731867598295,0.7305412666722806,0.735069793917828,0.739785151974836,0.7445399159710036,0.7492183772903924,0.7537394305785694,0.7580578631736717,0.76216476934108,0.7660875578629084,0.7698898143535313,0.7736711006668701,0.7775666056214358,0.7817463872878206,0.7864137500928549,0.7918020611324494,0.7981690073605597,0.8057869018547071,0.8149271290793161,0.8258361316405006,0.8386994268543917,0.8535889491741222,0.8703882447004543,0.8887062969502557,0.9078665041465168,0.9270132223139549,0.9452407224411628,0.9617054705852877,0.9757200066225893,0.9868216142450801,0.9948034497135534,0.9996992014680397],[0.7912972789929252,0.7847822795725989,0.7779663219689283,0.7709183333660357,0.7637293775046555,0.7565145365442267,0.7494136639710525,0.7425902633821853,0.7362274764866834,0.7305198823761744,0.725659726461634,0.7218170562681889,0.7191167407008396,0.7176215182291953,0.7173303661671624,0.7181890597345066,0.7201005824924441,0.7229283628411947,0.7265000564089312,0.7306237855674214,0.7351088145174729,0.7397809345096182,0.7444920879316146,0.7491259113541355,0.7536006346639584,0.7578703823055386,0.7619256015552014,0.7657930883975159,0.7695358745091387,0.7732530601877655,0.7770795103978622,0.78118515771309,0.7857734596349655,0.791078319659803,0.7973584794762908,0.8048879967408339,0.8139409045335877,0.824767459565981,0.8375584656344441,0.8523929308458761,0.8691630868607323,0.8874846875566208,0.9066837490499564,0.9259069584304765,0.9442507010458839,0.9608712595846546,0.9750762028438661,0.9863916312153711,0.994595071441238,0.99970465823552],[0.7914874988552022,0.7849975735111873,0.7782087623426189,0.7711897472001503,0.7640311538597644,0.75684736784057,0.7497772069693532,0.742982708906593,0.736645032087307,0.7309562188772616,0.7261055616607693,0.7222602876072213,0.7195436853233919,0.718019183089716,0.7176885441832792,0.7185013095213063,0.7203642132239418,0.7231434752134788,0.7266677983670771,0.7307452924795698,0.7351848986742074,0.7398119636223712,0.7444779103050527,0.7490658049326465,0.7534932746609742,0.7577138261168904,0.7617172918223093,0.7655298770887847,0.7692140730595514,0.7728685232050507,0.7766277633062526,0.7806615820523767,0.7851735536351605,0.7903980561959356,0.79659478849943,0.8040394045066176,0.8130083667472972,0.8237554284986914,0.8364762289927866,0.8512562385612479,0.8679957727327966,0.8863173126091167,0.9055500998659444,0.9248439305601773,0.9432978059250241,0.960068033699117,0.9744572354204212,0.9859803115462468,0.994399175367448,0.9997165289619655],[0.7916930023406286,0.7852301968261549,0.7784707605423223,0.7714831174695709,0.7643574308567005,0.7572073497050273,0.7501705980093925,0.7434076698149505,0.7370976467964077,0.7314299393426418,0.7265908179740201,0.7227446712534165,0.720013204164575,0.7184604665204282,0.7180908891209459,0.7188576869760028,0.7206713218091179,0.7234008783722377,0.7268762295162586,0.7309056548761103,0.7352979585001377,0.7398781934857046,0.7444973784454139,0.7490380949452893,0.7534174306208201,0.7575883205773817,0.7615400161195467,0.7652981554183762,0.7689247040166096,0.7725178549445695,0.7762118112577653,0.7801762012748212,0.7846146814680313,0.789762044836058,0.7958788513761632,0.8032422044859634,0.8121307775025097,0.8228015013368305,0.835454393118971,0.8501807460021213,0.8668882338822164,0.8852059455178701,0.9044670851575595,0.9238253804452634,0.9423829680377338,0.9592964285817216,0.9738635219654621,0.9855879718863477,0.9942160260609016,0.9997349136280196],[0.791913562207216,0.785479877919011,0.778751992882726,0.7717980598572696,0.7647077544751437,0.7575939494506484,0.7505932181165604,0.7438644367690684,0.7375845239197654,0.7319401743910925,0.7271145826223797,0.7232692912397297,0.7205244211882151,0.718944575692798,0.7185367291988926,0.7192576611446638,0.7210215068780603,0.7237002657968494,0.7271251095727513,0.7311046867956794,0.735447857240681,0.7399795336936885,0.7445504466445736,0.7490427797635031,0.7533731454368573,0.7574939546759342,0.7613939123137454,0.7650981141999063,0.7686680165727775,0.7722013698445278,0.7758320422957201,0.7797294869082741,0.7840974095172399,0.7891709595601131,0.7952114635180489,0.8024973279414703,0.8113092180329616,0.8219069215679323,0.8344943710109973,0.8491680257992155,0.8658420871960997,0.8841520468557014,0.9034359407703045,0.922852275676857,0.9415068575415304,0.9585568265578376,0.9732952282233717,0.9852146777498137,0.9940456508756911,0.9997597003560508],[0.792148938329063,0.7857463301778994,0.7790521183224428,0.77213417018888,0.7650816482850271,0.7580066095590081,0.7510444214645831,0.7443522722931873,0.7381048383142701,0.7324860266047721,0.727675914722688,0.7238332013159559,0.7210764251374744,0.7194706751314903,0.7190253417342827,0.7197006443952516,0.7214143085340978,0.7240412709311947,0.7274141398315469,0.7313421482028264,0.7356344089650235,0.7401158491065011,0.7446370280308905,0.749079819108015,0.7533604247069579,0.757430780224887,0.761279079887273,0.764929903205452,0.7684442146032533,0.7719193309012421,0.7754887847426637,0.7793218399301848,0.7836222197300038,0.788625372334813,0.7945932962752004,0.8018055546211666,0.8105445841482224,0.821072705904201,0.8335973000470911,0.8482193251897537,0.8648586049364675,0.8831567490807112,0.9024576029655539,0.9219253067281337,0.9406698819697659,0.9578493527906619,0.9727522582538823,0.9848602247918243,0.9938878152306665,0.9997905399113258],[0.792398878280259,0.7860292527225154,0.7793707794133105,0.7724910256388562,0.7654786149696069,0.7584447495812706,0.7515235376995666,0.7448704135145064,0.738657739433142,0.7330665736335122,0.7282738481797395,0.7244354275179777,0.7216682717468602,0.7200378884164383,0.7195559538368649,0.7201859914565554,0.7218492065082172,0.7244234651609036,0.7277429620777507,0.7316177445635422,0.7358573784492077,0.7402869598526518,0.7447569945978332,0.7491491340571935,0.7533792366963497,0.7573988117614293,0.7611955797652454,0.7647936309053309,0.7682534563024181,0.7716719491818086,0.7751823065622873,0.7789535899426383,0.7831895085558204,0.7881257517460609,0.7940248951576259,0.8011675103983479,0.8098375829803738,0.8202996394669585,0.8327640338000475,0.8473355475598194,0.8639386862392497,0.8822208468349276,0.9015327051917515,0.9210448866527207,0.93987218675087,0.9571738739488949,0.9722342474935742,0.9845241225457669,0.9937419986224826,0.9998268205510695],[0.7926631179349503,0.786328331166364,0.7797076032667434,0.7728681859504432,0.765898137853713,0.7589077680266887,0.7520298742199578,0.7454180748113217,0.7392423542202496,0.7336808711060602,0.7289073943902362,0.725074970588495,0.722298985858824,0.7206452998609992,0.7201277431616574,0.7207129983437419,0.7223256178719248,0.7248463557252569,0.7281111577817133,0.7319311266917267,0.7361164812731987,0.740492641498423,0.7449101773671523,0.7492506071689242,0.7534295124023379,0.7573980265473192,0.7611434342450543,0.7646893643222495,0.7680958539560383,0.7714593835056485,0.7749128149389907,0.7786249946356151,0.7827995862756182,0.7876724621716323,0.793506678821681,0.8005836660265215,0.8091887314224663,0.8195882737041578,0.8319951387842586,0.8465172447525302,0.8630828422756438,0.8813447943247655,0.9006615787994221,0.920211153570143,0.9391136582094916,0.9565299996577322,0.9717405592398011,0.9842055813803969,0.9936073715708894,0.9998676431356838],[0.7929413820810222,0.7866432383929296,0.7800622025325381,0.7732651946634042,0.7663396824294689,0.7593950442293846,0.7525627184030447,0.745994450362395,0.7398577898555747,0.7343279553626958,0.7295755447819472,0.7257508082782116,0.7229675634849833,0.7212919562317855,0.7207398388527384,0.7212809014404655,0.7228428942798404,0.7253093838256452,0.728518247709458,0.7322818909141002,0.7364113841504929,0.7407326253923245,0.7450963666900289,0.7493840827175836,0.753511145721699,0.7574283646673788,0.7611226270286371,0.7646171290003279,0.7679714738498994,0.7712817402958545,0.7746804560763487,0.7783362395402255,0.7824526767238321,0.7872657634978603,0.7930389388276959,0.8000543370206376,0.8085983562832258,0.8189389271090101,0.8312908964146684,0.8457646228757028,0.8622912084576702,0.880528710435746,0.899844257805398,0.9194239759809658,0.938393929134624,0.9559170869585762,0.9712702850845436,0.9839035036307116,0.9934827739490613,0.9999117964153743],[0.7932333850448982,0.7869736353424125,0.7804341763857203,0.773681580343806,0.7668026978724309,0.7599059401853812,0.7531213397703752,0.7465987165934524,0.7405031363557841,0.7350068460236654,0.7302772732094012,0.7264618975532594,0.72367297384699,0.7219768685682217,0.7213913228073998,0.7218888771369243,0.7234003187169791,0.7258119233708079,0.7289636920792423,0.7326695795941993,0.7367417055047912,0.7410065991900915,0.7453153126882819,0.7495493670468087,0.7536239937208897,0.7574897292267253,0.7611331033574081,0.7645769090889204,0.7678803363147955,0.7711390736002139,0.7744853152142257,0.7780874380713405,0.7821489174021716,0.7869058113778113,0.7926218401637783,0.7995796846544266,0.8080665961358559,0.8183516886830726,0.8306513099686019,0.8450775596518879,0.8615635736428352,0.8797723910825762,0.8990804875886188,0.9186829608691283,0.9377123869380812,0.9553342479330172,0.9708222497790223,0.9836164800554448,0.9933666956421103,0.9999577324042321],[0.7935388313250056,0.7873191718058028,0.7808231115172303,0.774116857810547,0.7672866185417604,0.7604398023529396,0.7537049920860746,0.7472300345186103,0.7411774690352204,0.7357165484074396,0.7310115382252342,0.7272071767311399,0.7244141614261214,0.7226990141486631,0.7220812313689124,0.7225360424869836,0.7239971022336705,0.7263532809255328,0.7294468913731114,0.7330936820449747,0.7371070163031049,0.7413142075631237,0.7455667258362293,0.7497462290378292,0.7537678770085713,0.7575819866461563,0.7611747702492386,0.7645686475405653,0.7678224159070428,0.7710313852807537,0.7743274168627546,0.7778786318567157,0.7818883599801487,0.7865926580222901,0.7922554225198781,0.7991597180427459,0.8075934047935228,0.8178264239686418,0.8300761159069436,0.8444556285057994,0.8608994120624103,0.8790753273529366,0.8983697371911515,0.9179874644645462,0.9370681843607616,0.9547803605629552,0.9703950209229134,0.9833427929264231,0.993257261368144,1.0000035417525293],[0.793857416231525,0.7876794872231845,0.7812285831244747,0.7745705293537173,0.7677908654587097,0.7609959634102981,0.7543129153834651,0.7478875519760849,0.7418798508334887,0.736456055812051,0.7317772852440321,0.7279855675637709,0.7251900480440208,0.7234573386357296,0.7228085575178542,0.7232214572410249,0.7246323848803372,0.7269326973294948,0.7299671878684473,0.7335536358448861,0.737506841148651,0.7416550530903805,0.7458502776822309,0.7499744006921687,0.7539425802092685,0.7577049670545656,0.7612474968363608,0.764592246421801,0.7677976417229486,0.7709586253696248,0.7742067252499161,0.7777097913474383,0.7816709711738535,0.7863262535090595,0.791939602285812,0.7987942972582314,0.8071785563031889,0.8173627833765661,0.8295647986349477,0.843898125198127,0.8602979140594614,0.8784367276112734,0.8977112147351267,0.9173366054616544,0.9364602526168755,0.9542540828028427,0.9699869237359645,0.9830804270870765,0.9931522229237815,1.0000469290264657],[0.7941888265301207,0.7880542114833069,0.7816501558980204,0.7750420859402816,0.7683148477583523,0.7615737439658693,0.7549443379166575,0.7485704057587773,0.7426093345163005,0.7372243516717827,0.7325734486131634,0.7287959772824313,0.7259995349899862,0.7242507584175466,0.723572253581971,0.723944127319807,0.7253052425340663,0.7275493510657906,0.7305238678954932,0.7340488285556158,0.7379406596304113,0.7420286973307113,0.7461656017073093,0.7502335778265387,0.754147852536315,0.7578584647767259,0.7613511148025447,0.7646475673350259,0.767805897844938,0.7709206925881501,0.7741231449780038,0.7775808167023546,0.7814966339910391,0.7861064475900734,0.7916741752373352,0.7984831374141075,0.8068216513153844,0.8169602124659353,0.8291166076975938,0.8434040946516821,0.859758015217774,0.8778555418559472,0.8971038853674593,0.9167292804244259,0.9358873168006604,0.953753869734863,0.9695960609812828,0.9828270901452986,0.993048963878015,1.0000851878049808],[0.7945327410874354,0.7884429657216112,0.7820873850009518,0.775531008402992,0.7688579641101223,0.7621724542168544,0.7555984780348683,0.7492777236412903,0.7433649647564238,0.7380204116003617,0.7333989536027916,0.7296373006156326,0.7268415052031414,0.7250781631453429,0.7243712344324909,0.7247030094671111,0.7260146946257309,0.728202363012709,0.7311161647652651,0.734578599822413,0.7384079079196573,0.7424346620695619,0.7465122943166427,0.7505234208767829,0.7543834084615698,0.7580422389142422,0.7614854189174062,0.7647344319490059,0.7678470239163393,0.7709174350249042,0.7740765218828889,0.7774915389370616,0.7813651493273787,0.7859329919713994,0.7914588198658593,0.7982258136303181,0.8065221246618883,0.8166179637950169,0.8287305764742967,0.842972356938442,0.8592784238965709,0.8773304870142897,0.8965464911108708,0.9161641810587965,0.9353479133189936,0.953277993568039,0.9692203378732911,0.9825802425240595,0.9929445228235874,1.0001151798186112],[0.7948888315162328,0.7888453631140616,0.782539817037685,0.7760367686088461,0.7694196041033294,0.7627913955530441,0.7562745459781615,0.7500086263056512,0.7441457801015312,0.7388432053306062,0.7342527183249804,0.7305084217873036,0.7277148255111113,0.7259384184528714,0.7252043810910317,0.7254970166403765,0.7267597113825336,0.7288908020047211,0.7317432622618518,0.7351422438224917,0.7389079805975433,0.7428724307310759,0.7468899159581445,0.7508435558067849,0.7546489284787475,0.7582560140169663,0.7616501676652087,0.7648526226351012,0.7679208158411572,0.7709486509677801,0.7740666440887025,0.7774417213261504,0.7812762378958631,0.7858055430359782,0.7912931013001802,0.798021766788684,0.8062792539568909,0.8163351099563425,0.8284055415955859,0.8426015320408629,0.8588576472293444,0.8768600722802663,0.896037572020468,0.9156398130007342,0.9348404090594199,0.9528245661339068,0.9688574915337406,0.9823371373717821,0.9928356400602001,1.0001333665902525],[0.7952567628181721,0.7892610096643015,0.7830069910092894,0.7765588306037995,0.7699991495943904,0.7634298621033181,0.7569717455940841,0.7507622291685305,0.7449508148355162,0.7396916985592447,0.7351336555896794,0.7314082164993019,0.7286183489207967,0.7268303688307023,0.7260705446429385,0.7263250237118106,0.7275392205832287,0.7296136906954647,0.7324042985629664,0.735739012014389,0.7394402326924114,0.7433414499439309,0.747297992360894,0.7511935751173632,0.7549440599565875,0.758499480841671,0.7618450839650545,0.7650018832057695,0.7680270266045199,0.7710140898841472,0.774093243249349,0.7774310610456256,0.781229542468709,0.7857236649754729,0.7911764757627968,0.7978703099747418,0.806092169029841,0.8161105574271984,0.8281401624879742,0.8422900632685107,0.8584940156467825,0.8764426239336931,0.8955754881020814,0.9151545157519911,0.9343630219588889,0.9523915634313824,0.9685051242798287,0.9820948694052916,0.992718828454816,1.0001359212718182],[0.7956361940223138,0.7896895049818227,0.7834884392526338,0.77709665173084,0.7705959760130479,0.7640871422230117,0.7576892759753326,0.7515376441130903,0.7457791007394967,0.740564854704407,0.7360406747033617,0.7323355538992146,0.7295509169517467,0.7277528406194343,0.7269685503421685,0.7271858731686803,0.728352113849331,0.7303700113915288,0.733098370444612,0.7363681161327422,0.7400039819010427,0.7438411312469282,0.7477360158848558,0.7515730389493545,0.755268418077514,0.7587722971943139,0.7620698559789265,0.7651819197514111,0.7681653672088974,0.7711134535424142,0.7741559959671755,0.777459191040895,0.7812246304089263,0.7856868332943033,0.7911082954991142,0.7977706354992886,0.8059598619989634,0.815943060902319,0.827932940622596,0.8420362393161365,0.8581857059798633,0.8760763093082873,0.8951584415238912,0.9147064833941492,0.933913842605766,0.9519768516893993,0.9681607397702404,0.9818504307693731,0.992590464149073,1.0001188591482768],[0.7960267788175643,0.7901304430490186,0.7839836883609363,0.777649683718892,0.771209453625343,0.7647625199208935,0.7584263330190959,0.7523339811287952,0.7466296687582857,0.741461636582118,0.73697268321429,0.7332892985317951,0.7305113619986741,0.7287046450806097,0.7278972017971619,0.7280783806251081,0.7291972524952066,0.731158711678602,0.7338245376355388,0.7370287313688332,0.74059851096492,0.7443708529184583,0.7482034469721872,0.7519814762743484,0.7556215868569104,0.7590740888517911,0.7623241380036234,0.7653924015711797,0.7683355077206286,0.77124639726759,0.774254525378147,0.7775256821043686,0.7812609964668592,0.7856944386465269,0.7910878141150588,0.797721822391248,0.8058811978020184,0.8158312378207042,0.8277822381809176,0.8418382149897703,0.8579307631946789,0.8757591597190293,0.8947844987325384,0.9142937857223847,0.933490856487837,0.9515782143544161,0.9678217808298208,0.9816007711338269,0.9924468894117268,1.0000781690635236],[0.796428166177393,0.7905834129751621,0.7844922600835534,0.778217373740383,0.7718389487515658,0.7654552762250125,0.759182110909156,0.7531503498626116,0.7475015505776299,0.7423810080070177,0.737928588606779,0.7342683122702274,0.7314985097068845,0.7296845815023933,0.7288552851414216,0.7290013400475619,0.7300734729594154,0.7319787097567485,0.7345818272076389,0.7377199996771764,0.7412230701707152,0.744929961912562,0.748699715689498,0.752418386165904,0.7560031202376599,0.7594044505586891,0.7626075514422508,0.7656329621929553,0.7685370784208031,0.7714125313227991,0.7743884028920341,0.777630045145592,0.7813380658155646,0.7857457909645529,0.7911141922573195,0.7977228442549578,0.8058549250135775,0.8157735828469243,0.8276862959542503,0.8416940306424084,0.8577271208063505,0.8754890922448785,0.8944516121599495,0.9139143894608371,0.9330919664926682,0.9511933793764842,0.9674856676502905,0.9813428586819686,0.9922845187106311,1.0000099459865166],[0.7968400009752666,0.7910479997355286,0.7850136722030892,0.7787991654356355,0.7724838249378163,0.766164690487103,0.7599558035221443,0.7539858610850206,0.748393780117005,0.7433219353215341,0.7389072999454547,0.7352714562217368,0.7325111813428,0.7306914402983467,0.7298415731114799,0.7299535286507761,0.7309795918390736,0.7328288994523987,0.7353692379128194,0.7384410331516138,0.7418768799436251,0.7455177758834025,0.7492242233497124,0.7528832391435467,0.7564125432541963,0.7597629470941835,0.7629196858505969,0.7659032004773113,0.7687696710540876,0.7716114224081435,0.7745571500754019,0.7777717336359402,0.781455197297852,0.7858401238377284,0.7911865035704766,0.7977725773889006,0.8058796867943298,0.8157684821143554,0.8276432503675002,0.8416016303656477,0.857572620015793,0.8752639303129458,0.8941576412730831,0.9135661792488717,0.9327150152738147,0.9508200461652908,0.9671498350415088,0.9810737384895514,0.992099938678806,0.9999105252058812]],[[0.08536583391667761,0.08149875398584801,0.07700869772947122,0.07185910198164103,0.06603824740962798,0.059575683713118555,0.05256885309925692,0.045229472615665296,0.037969412797105515,0.031553033938240375,0.02725108791491774,0.02646331904526456,0.02935647508028262,0.03457830196401563,0.04067843195348599,0.046793798551387336,0.052529996489157786,0.05775347079241324,0.06245484651171963,0.06666913490069401,0.0704327520396093,0.07376485510398889,0.07666376146321471,0.07911110897528537,0.08107857210807329,0.08253418741226382,0.08344712766313166,0.08379086882444178,0.08354519947190302,0.08269762811711984,0.0812446293419928,0.07919294646842893,0.0765608877242642,0.07337923297849518,0.06969103212602598,0.06554930140572728,0.06101160601329159,0.056131117090142,0.05094538863178343,0.04546691937427197,0.0396825559144655,0.03356953433634167,0.027132123314234508,0.020455291838503968,0.013765585809825683,0.007492766471784536,0.0024214612907267523,0.0018155107424616148,0.002432046900562667,0.0014909964715004822],[0.08526710377692905,0.08136969980121762,0.07683980293595996,0.07163752492031043,0.0657463730441847,0.059188869950134095,0.052051921238091665,0.04453163062800684,0.037019512359189814,0.030269311497632692,0.02561520598433905,0.024660271087677873,0.02766458205371574,0.03310130567334497,0.03938720430596551,0.045635898017927855,0.05146702206202804,0.056764983614509774,0.06153378116709839,0.06581590132742939,0.06965016454549486,0.07305463041800832,0.07602465334706272,0.078538341984269,0.08056409035475554,0.08206728399947037,0.08301515925398605,0.08337990339129117,0.08314055529828486,0.08228433372206113,0.08080787655284244,0.07871863303135844,0.07603635690827427,0.07279431206172961,0.06903943439531053,0.06483036007923251,0.06023212240366111,0.05530682714580616,0.050101273483611874,0.044635549414167794,0.03890016716221704,0.03287060108906918,0.026544221638631363,0.01999628471226471,0.01344488944039635,0.007321451002632227,0.002483821388639383,0.002015811638348247,0.0024553393650204236,0.0012235431318124899],[0.08517947810586263,0.08125486153869137,0.07668905103987778,0.07143902201495655,0.0654837117390759,0.05883877707132503,0.051580514909776935,0.043888500838145765,0.03613033011344991,0.029039133914373388,0.024000220565242442,0.022846577640754328,0.025966336808410727,0.0316269236361579,0.03809797918124075,0.044474688312588634,0.05039507119690911,0.05576338732376291,0.06059751271210447,0.06494721722716545,0.06885322366788366,0.07233192890860496,0.07537524253434764,0.07795740444714688,0.08004332811372973,0.08159565371787732,0.0825796520114512,0.08296622274824407,0.082733661355828,0.08186889211510529,0.08036869254396752,0.07824117475545699,0.07550748477301732,0.07220333030572551,0.06837955022141641,0.06410054511002494,0.05943918119561095,0.05446717222618863,0.049241568752654605,0.04379128033798477,0.03811170896676209,0.032177580767431435,0.025980292887439183,0.019587040142308377,0.013212354699327258,0.007307281151574894,0.002873897035622493,0.002423910210160054,0.0025735763767537716,0.0010785081494873506],[0.08510317121214736,0.08115454660207118,0.07655688917383863,0.0712642555929308,0.06525126797755489,0.058526974610431104,0.0511571754590557,0.04330434492895806,0.03530906391914734,0.0278732850231789,0.022415464986833868,0.021024437585829458,0.0242641719803456,0.030157932207452526,0.03681236039168974,0.043310684652118146,0.049314016946255805,0.05474829036474891,0.0596456363132385,0.06406280169131975,0.06804182125407031,0.07159680678632402,0.07471571356868446,0.0773685675154072,0.07951660818666434,0.08111964755786964,0.08214097310247988,0.08255020733662753,0.08232491439283195,0.08145172184799902,0.07992752179019362,0.07776104017706237,0.07497475029454749,0.07160674481742385,0.06771175702893381,0.06336006783586834,0.058632719998838186,0.05361171295336814,0.048365404205157975,0.04293285362490807,0.037315685878679526,0.03148894821763275,0.02543892780158096,0.01922613959557072,0.013065408760414185,0.007438245292784844,0.003456910179150855,0.0029275082076158005,0.002747709544701848,0.001031545720006018],[0.08503837016432145,0.08106902441942566,0.07644371125820681,0.07111381309501484,0.06504994082667745,0.058254885696510106,0.050784252476670656,0.042783227962879436,0.03456295487932195,0.02678365225021034,0.02087254836622886,0.019196404953089597,0.022560876717149125,0.02869740535633911,0.035532003698046925,0.0421443531454428,0.04822366885643608,0.05371925766495867,0.05867773358454844,0.06316238796816653,0.06721588288077146,0.0708493641459182,0.07404629728858801,0.07677214612273069,0.07898429239168993,0.08063965047154383,0.0816995195442626,0.08213226498585266,0.08191473814716023,0.08103327042144641,0.0794848422819673,0.07727873868098836,0.07443868325826608,0.07100507524796708,0.06703650610113399,0.06260922022398814,0.0578127534127163,0.0527400674344976,0.04747193116629576,0.042058987788106496,0.036510537293165175,0.03080306742216988,0.024918497418066347,0.018911565389817846,0.012999445291148385,0.007694308290012943,0.004130941670909484,0.003465146695527577,0.002948761544434647,0.0010399702521909533],[0.08498523366109083,0.08099852459997152,0.07634985489807611,0.07098820164223986,0.06488051395142344,0.05802376760582276,0.05046386349362235,0.04232893134140475,0.033899115593457846,0.025783111473694206,0.01938600928242873,0.017365528949343106,0.02085970450978592,0.027248763463469456,0.03425861455079758,0.04097610314746887,0.04712376917560216,0.05267581121941114,0.057693376535483,0.06224572929795374,0.06637537409761614,0.07008975054744415,0.07336727523255063,0.07616850214936004,0.07844678366966537,0.08015608268389099,0.08125571897152253,0.08171283134624216,0.08150358362049456,0.08061401457225942,0.07904116603416583,0.0767948215272496,0.07389986623676802,0.07039890731193073,0.06635432831414623,0.06184838331433661,0.05697938401133981,0.05185192354575368,0.04656033424254386,0.041168389043026755,0.03569465013546656,0.030118211824859176,0.024417184380572717,0.01864075029622657,0.013008085189668837,0.008051471110218925,0.004840769092580141,0.004008164854030882,0.0031590613637869818,0.0010663653607354082],[0.08494389105026058,0.08094323532298699,0.0762755986480939,0.07088784319253426,0.06474364656940604,0.05783469371509493,0.05019785508482173,0.04194486272949526,0.03332432456669251,0.02488527460617691,0.017974105922801076,0.015535590194674775,0.01916453458788449,0.025815834267477994,0.03299394626583151,0.03980627997246631,0.04601398968065771,0.051617431448178756,0.05669213237939258,0.061312605561190114,0.06552030730420803,0.06931817099828981,0.07267898423786424,0.07555804763454155,0.07790452815312954,0.07966940092371719,0.08081003030372118,0.08129237021039915,0.0810919292289774,0.08019446041939857,0.07859703943109703,0.07630988269300404,0.07335893638201033,0.06978889617548643,0.06566583990180035,0.06107803600430344,0.05613281409100501,0.05094705231064334,0.045629844114317565,0.04025976276900956,0.03486637261837281,0.02943258745471278,0.023933021229222366,0.018410653174310534,0.013083594775669697,0.008485649299145203,0.005558360769707516,0.0045434786237909695,0.0033694705051623038,0.0010899438209617468],[0.0849144415075575,0.08090330198011299,0.07622115968777497,0.07081307037789814,0.06463986555431031,0.05768853737749067,0.04998776680448015,0.04163396691406923,0.03284479400884514,0.024104060478638775,0.016659675306173422,0.013711519834960974,0.01748012003807066,0.024402929158258396,0.03173979908111583,0.03863515825646252,0.04489392926115931,0.05054355941835938,0.05567356928858645,0.060362830807893,0.06465074929484724,0.06853489233827585,0.07198182121605835,0.07494124801321603,0.07735801717500589,0.07918009955511765,0.08036294429675345,0.08087137371014677,0.08068028081782941,0.07977514345470336,0.07815304338876397,0.07582455950248865,0.07281658699284684,0.06917576966237421,0.06497174819660702,0.060298764142242486,0.05527335820663035,0.0500253224678974,0.04467975148586766,0.03933182572017315,0.03402402890674376,0.028744358619859772,0.02346393485178285,0.01821785610051819,0.013217388342034007,0.00897520088246955,0.006269155664396745,0.005065186686956446,0.0035761849883887272,0.0011038579102467677],[0.08489695338507931,0.0808788260896544,0.07618669194486856,0.07076412310321822,0.06456955887857775,0.05758595821676732,0.049834799397584964,0.041398642205672735,0.03246592384911189,0.023453065030985463,0.015470853577223845,0.011900187807908547,0.01581248021998862,0.023014938620594574,0.03049802071127208,0.03746293631260682,0.04376311239998329,0.049453600022983366,0.05463726318857863,0.05939626174073223,0.06376682950469932,0.0677402500258284,0.07127624808282423,0.07431862534907314,0.07680778919143987,0.07868871158877015,0.07991498396291077,0.08045036237570947,0.08026917152738659,0.0793566283639946,0.07770979331508658,0.07533953301653054,0.07227356881599191,0.06856033122045348,0.06427285728244049,0.059511269886418666,0.054401456521860785,0.04908671634292508,0.04370942230974289,0.0383833189505455,0.03316593451591471,0.0280516759426637,0.023007796097925998,0.018058676673824204,0.01340053575673615,0.009502006652381205,0.006965303915668882,0.005570786948928228,0.0037782450736223924,0.001109137030785944],[0.08489146373739924,0.08086986449834038,0.07617228469827103,0.07074114597564068,0.06453297056053885,0.057527391283768554,0.049739788659245165,0.041240667280206804,0.03219206009552061,0.02294474186800764,0.014441196287355504,0.010111990999854013,0.014169540186108253,0.02165745106916926,0.0292705092300771,0.03628973188130484,0.0426209886886954,0.04834692621007521,0.053582805692725444,0.0584128072311531,0.0628687489905167,0.06693465531816904,0.07056279681456475,0.07369076153164499,0.07625443159034925,0.07819580955078614,0.07946670484217426,0.08002988504355077,0.07985916149798666,0.07893950866426813,0.07726793884858647,0.07485552815223757,0.07173069103560174,0.06794346258515586,0.06357007348322607,0.05871638127257158,0.053517688993731945,0.04813134715863574,0.042718314442825575,0.03741302143407553,0.03229041226969964,0.02735270653841556,0.022562473467188034,0.017929288283396527,0.013624211040114114,0.010051561890124544,0.0076424663459766975,0.006059413118189493,0.0039758695760645614,0.001109512760451884],[0.08489797803149206,0.08087642888249746,0.07617796168504631,0.07074418661891554,0.06453019724890913,0.057513039443722415,0.04970318614147989,0.04116114318397718,0.032026279345500466,0.022589458669601856,0.013608402278545477,0.008364323461347778,0.012562204680676441,0.020336899210983226,0.02805921937022567,0.035115579737635814,0.04146693350926263,0.04722288435614842,0.052509813289613134,0.05741243895492404,0.06195679017779759,0.06611860283232365,0.06984207459716418,0.07305830140029813,0.07569858235438616,0.0777020061853905,0.0790186951072903,0.07961051859915652,0.0794508374012643,0.0785244061429199,0.07682816335608907,0.07437331350276796,0.07118882190398645,0.06732612606946381,0.06286441059922142,0.057915061916689665,0.05262279040576434,0.04715947794632099,0.04170599594238313,0.03641976438396147,0.03139580865001114,0.02664566620651142,0.02212588978373571,0.01782584116382031,0.013880044341358025,0.010612578579445,0.008298244003329278,0.006530980874637896,0.00416950525840586,0.0011076281618372878],[0.08491647004466255,0.08089848555680236,0.07620368072849455,0.07077319491073687,0.06456118653942748,0.05754286926585865,0.04972504764071972,0.04116045453961213,0.03197022195008448,0.022394556626907546,0.013010674704002297,0.006689892569124406,0.011006213633054809,0.01906073667076695,0.02686617363411877,0.03394043168236875,0.04030025000270031,0.04608080088058819,0.05141793791020639,0.05639520324233975,0.06103132740427198,0.0652926784662786,0.06911476902511848,0.07242195575279026,0.07514093154408005,0.07720795496632729,0.07857157548461409,0.07919286754107747,0.07904481178571493,0.07811197008536926,0.07639118317032137,0.07389370082672528,0.07064888896360876,0.06670936640320882,0.062156994788266605,0.05710842075913121,0.05171766625189213,0.04617154224492894,0.04067216527672065,0.03540244630983397,0.03048051038399678,0.025928853609159502,0.021696080860251536,0.017744577910247354,0.014160366271069265,0.011176432114447923,0.00893136681493146,0.006985773655904351,0.0043594481913051975,0.0011034501008389797],[0.08494688195258306,0.08093595559479684,0.07624933389609584,0.07082802316335672,0.06462573707599262,0.05761661057364874,0.049805030055713274,0.041238252822940705,0.03202399316799596,0.02236358375037092,0.012680322651776217,0.005158468922591062,0.009525409935202782,0.01783764350671574,0.025693479950979845,0.032764159511292176,0.039120172429355046,0.04491999020180498,0.0503068790211027,0.05536123424872066,0.06009283828651077,0.06445756765053957,0.0683816533007154,0.0717825041905072,0.07458222256400547,0.07671435039065849,0.07812599897241018,0.07877756335274867,0.0786417222248786,0.07770287627811387,0.07595774654893026,0.07341754417679791,0.07011187880860803,0.06609431203768902,0.06144906897366687,0.05629772173124081,0.05080340945595078,0.04516816680671321,0.03961667380974574,0.03436004889882391,0.02954296113639434,0.02520068656369183,0.021271255312397493,0.01768193851498566,0.01445835297275446,0.011736622111013619,0.009541252948112679,0.007424252365600375,0.004545865146260247,0.0010954432016280816],[0.08498912460742226,0.08098871526124411,0.07631474818775842,0.0709084272492385,0.06472350044376297,0.057733759690977,0.04994239681125899,0.04139346304884427,0.03218614467062794,0.022495869676791423,0.01263598514642173,0.003933548144179389,0.008157453793874192,0.01667774998521896,0.024543357975696335,0.031586561634332606,0.037925871004978295,0.04373976414431505,0.049176397415717416,0.05431076856302416,0.05914191593181035,0.06361406388934093,0.06764359137341594,0.07114079774662295,0.07402325317195556,0.07622192802758143,0.07768265033821688,0.07836526366901185,0.07824223025720499,0.07729782577518055,0.07552863233745966,0.07294573863785081,0.0695788363327896,0.06548217582508499,0.06074199664326447,0.05548439319535683,0.04988131788530269,0.04415019655749154,0.03853955102699245,0.03329165387191178,0.02858167820510586,0.0244597407779101,0.020849854890441756,0.01763465160737401,0.014768090680755354,0.01228831237212738,0.010127758270078188,0.00784697730609004,0.004729017868902529,0.001082983445286344],[0.08504307800391013,0.08105659675228631,0.07639968674636329,0.07101406865488062,0.06485398481634222,0.05789358629419642,0.05013603163156086,0.041624313495438096,0.032453739143084956,0.022786546163854834,0.012876957563625814,0.003354751188555426,0.0069630314555952,0.015592849831958147,0.023418176469761975,0.030407374108434453,0.036716458272108114,0.04253944292018001,0.04802633090870334,0.05324416138638968,0.05817928201069921,0.06276307753743361,0.06690154294888656,0.07049776123728763,0.07346487618838292,0.07573146429410682,0.07724224537704895,0.07795665122491113,0.07784702010760987,0.07689754341716254,0.07510464832025378,0.07247921864587617,0.06905086341050734,0.06487425497619896,0.0600372648859789,0.05467003697289925,0.04895291257972546,0.04311872208812765,0.03744103310875215,0.03219646105695039,0.027595269158032173,0.023704791624689185,0.0204306149159046,0.017599810148670812,0.015084581373589962,0.012827962408741058,0.010691027101883873,0.008254577941580337,0.004909504239478403,0.0010688852896771099],[0.08510859192908049,0.08113938923531117,0.07650385057433842,0.07114451742782048,0.06501656027542196,0.05809514365993364,0.0503844600536494,0.04192838643435337,0.03282249049078423,0.023227011311890058,0.013383026929475902,0.003718822800038419,0.006036413279733471,0.014596542597018584,0.022320504478550187,0.029226286969159986,0.035490997038492775,0.04131836783149758,0.046856612182691465,0.052161904428161404,0.057205800695630644,0.061905644742306816,0.06615656828521371,0.06985439526963186,0.07290799986088439,0.07524377592897113,0.07680552991267643,0.07755243257523728,0.07745679718194852,0.07650277609358039,0.07468662924514238,0.07201895586111061,0.0685291169573581,0.06427193019503732,0.05933648649303387,0.0538564367324675,0.04801995656438719,0.04207510997627361,0.0363215956318962,0.031073808044544737,0.026582448401378328,0.022934859898927722,0.020012624615282727,0.01757493115077213,0.015403709311278917,0.013353041355564463,0.011231398278996618,0.008647732343150728,0.005088381024410358,0.0010613054149462898],[0.0851854867893918,0.08123684017654512,0.07662688073214845,0.0712992559648509,0.06521046568100751,0.05833728199079631,0.0506858777293329,0.04230268643433955,0.03328696353550095,0.023805729852667823,0.014119975729696404,0.004799836276823784,0.005501320437810659,0.013704197331259306,0.02125317913179471,0.028042966916049336,0.03424850988469612,0.04007591587695276,0.04566728909338764,0.05106464568400739,0.0562224934575835,0.06104293646238738,0.06540983268067432,0.06921177783400369,0.07235358783637137,0.07475971913608663,0.07637327852502022,0.07715333657449391,0.0770722863271287,0.076114290741195,0.07427543451015561,0.07156595657133343,0.06801480631932677,0.06367666388515945,0.05864140093186079,0.05304556546019752,0.047084474044314074,0.04102103624743946,0.035181991405659446,0.02992319196806623,0.025542053738205357,0.022149262951342993,0.01959538729293401,0.017557999944517306,0.01572218430906424,0.013861808939561333,0.011749341927361701,0.00902713634013118,0.005267102446432403,0.0010739198258388264],[0.08527355460699644,0.08134865694074639,0.07676836098735171,0.07147768357418567,0.06543481693530581,0.058618664411757386,0.051038184299818996,0.042743721827498374,0.033840811767138504,0.024509199587604783,0.015047483352310202,0.0062198933023482495,0.005458336312509536,0.012932574016155322,0.02021939270059318,0.02685708765777983,0.03298799021337217,0.03881151650045553,0.044458547812717505,0.049953211278390204,0.055230554693000374,0.06017626744868525,0.06466261054307496,0.06857106540159162,0.07180265869191688,0.07428018836923644,0.07594629298789388,0.07676011260847256,0.07669422985139017,0.07573287207315743,0.07387194550344611,0.0711212586049589,0.06750918994220735,0.06308999732108238,0.057953873982141954,0.05223959167801962,0.0461487696822315,0.03995852327215586,0.03402329472988729,0.02874429419850486,0.02447306306857102,0.021347673184683766,0.019178880339779377,0.017547500097443203,0.016037473272555412,0.014353148476681515,0.01224541388089382,0.009393456458316702,0.005447278277616759,0.001122732369160801],[0.08537256017513736,0.08147450864404822,0.07692782087644354,0.07167912173118096,0.06568861645481797,0.05893778516321018,0.05143902145684455,0.043247594453785496,0.0344770303774211,0.025322912334351053,0.016125800290104346,0.007781567866361497,0.0059019947180342525,0.012298906493843496,0.019222800810021066,0.025668369603056646,0.03170841478512076,0.03752467080154948,0.043230739284414205,0.04882862957042071,0.0542313681269537,0.05930710504997311,0.06391628891521686,0.06793349344264975,0.07125628497425433,0.07380611473069035,0.07552540040293905,0.07637352857047905,0.07632338530139611,0.07535932003651363,0.07347706259109513,0.07068592773811593,0.06701357127803152,0.06251354667898266,0.057275895806832774,0.05144088401254923,0.045215447536443,0.03888998034644728,0.03284695372034154,0.02753700910617087,0.02337461151213465,0.020530186677356708,0.018763614985403687,0.01754243031059067,0.016347727700941523,0.01482643937240911,0.012720221248535507,0.009747271167196259,0.005630314139744455,0.0012193684766869798],[0.08548224236102787,0.0816140282380706,0.07710473913621531,0.07190281993660037,0.06597076364406805,0.05929298947483902,0.05188581373311357,0.04381009282489619,0.035188204024398845,0.02623218275379566,0.01731961922891914,0.009401544284194787,0.006721282406323296,0.01181930674498736,0.018267652056677366,0.024476631163577078,0.030408757662895705,0.03621497364688089,0.041984409587442074,0.04769215773567151,0.05322652390240723,0.058437077669391047,0.06317237031470632,0.06730037627520682,0.07071559169770394,0.07333846395803488,0.07511145101769318,0.07599436857746818,0.07596052299522758,0.07499444699859706,0.07309170175156034,0.07026105358553497,0.06652929389209955,0.06194899782519791,0.05660957721784186,0.05065201364960853,0.04428742907475333,0.037818248094236444,0.03165485278777541,0.02630147857420194,0.022246009423197374,0.01969740573168393,0.01835069541046351,0.017542309581886874,0.016651711877689063,0.01528145941812901,0.013174396460719927,0.010089011325457926,0.005817034823084714,0.001365133768317063],[0.08560231554315266,0.08176681480092461,0.0772985474569285,0.07214796207854093,0.0662800661511348,0.059682494587848973,0.05237581058773159,0.04442678429522764,0.035966733399165084,0.02722278097507779,0.018599463035635387,0.011042229397197765,0.007784452289004182,0.011506571584196457,0.017358936140312902,0.0232818548231873,0.029088005471731966,0.03488213929598768,0.04072033495612572,0.046545311043067535,0.05221783621717104,0.057567982662919175,0.06243247472945936,0.06667310614974532,0.07018175425110333,0.07287823397587495,0.07470531571832799,0.07562343042393024,0.07560642331314348,0.0746390746662398,0.07271679086019063,0.06984774497178305,0.06605773574325124,0.06139809976933441,0.055957143888305215,0.04987575413955342,0.04336796947906332,0.03674664663146767,0.030449387894961166,0.025038134749777768,0.021086762056074078,0.018850540508418955,0.017941876274528902,0.01754717169595395,0.01694873431359391,0.01571830961367549,0.013608579192443572,0.010418912763046639,0.006007395590718593,0.0015513754935356475],[0.08573247116871688,0.08193243600872446,0.07750863450630434,0.07241367319412187,0.0666152516797414,0.060104411400250565,0.0529061284553244,0.045093102571209444,0.03680503028379645,0.028281359680829073,0.019941577284002615,0.01268463644574562,0.008992758188665068,0.01136785243768316,0.016502542178436715,0.022084272482901048,0.027745173876988456,0.03352603140723859,0.03943956239883707,0.04538989503972764,0.051207361306327706,0.05670179342721483,0.0616983405933771,0.06605315147229836,0.06965599566633945,0.07242645199225287,0.0743078831907366,0.0752615227743376,0.07526187375105922,0.07429403074548635,0.07235326563246684,0.06944712478721499,0.0656003026214142,0.060862656701926435,0.055320928263423504,0.049115077950988746,0.04246067120969422,0.03567902709954797,0.02923355784591963,0.023747754746279246,0.01989659209568519,0.017991536689960994,0.017539616801759778,0.01755754977223635,0.017238583548695032,0.01613735612586872,0.014023406410411752,0.010736992134722817,0.006200352722406964,0.0017645409759305506],[0.08587237941600462,0.08211043075971677,0.07773435017118942,0.07269902652485713,0.06697498013465583,0.060556766237830705,0.05347379159124984,0.04580442779163526,0.03769567619304339,0.02939570126212064,0.021327170607033596,0.014318168334254783,0.010283877810025311,0.011402982360275541,0.015705410165486995,0.0208844766569662,0.02637932519772059,0.03214669865729177,0.03814345709696995,0.04422804082896914,0.05019741548471008,0.055840665375906366,0.06097182455052576,0.06544205406720614,0.06913958320452429,0.07198417112373001,0.07392005674734564,0.07490946209829397,0.07492766574508447,0.0739601453535862,0.07200206524039046,0.06906032434192139,0.06515842074033665,0.06034451855527466,0.05470335893232745,0.04837314911144632,0.041569493508897166,0.03461982565270943,0.02801107555311881,0.0224315329281049,0.018675467022840713,0.017123238368154495,0.017147128223646682,0.01757445125402345,0.01752146848986282,0.016539185339530367,0.014419510789926452,0.011043052710373175,0.006393910223434437,0.0019904318209088487],[0.0860216909456766,0.0823003119221497,0.07797500996277218,0.07300305076015727,0.06735785588581401,0.0610375222981461,0.05407577074809069,0.0465561573427685,0.0386315441028892,0.030554825747273272,0.022741499075509014,0.01593643792321267,0.011620248492707364,0.011604203516407554,0.014975645807548966,0.01968356723687109,0.024989587110194163,0.030744417745409314,0.03683375805930863,0.043062243565003586,0.04919059285721667,0.05498694045008233,0.06025489980174754,0.06484142538195627,0.06863382422095668,0.07155246653814545,0.0735427508212896,0.0745680693562205,0.07460459127912192,0.0736382471994153,0.07166412762266673,0.06868847724087493,0.06473352849978427,0.059845570050956094,0.054106947247345966,0.047653311231830135,0.04069875619609538,0.03357411819767608,0.026786503890384946,0.02109117947074798,0.017423634579414354,0.016249598020437284,0.016768409550456893,0.017599323420179083,0.017797962910229042,0.016924568870369694,0.014797527202480568,0.011336721199784487,0.006585312598369542,0.002216142213818275],[0.08618003872455725,0.08250156917652808,0.078229899531344,0.07332473736640512,0.06776243995087415,0.06154460037182672,0.05470901893932997,0.04734376643346462,0.0396058858654386,0.03174900132527637,0.02417302062842795,0.01753538548616495,0.012979109671047862,0.01195747999823648,0.014322552601985577,0.018483348305831173,0.023575172473064815,0.02931974634820993,0.03551264385716983,0.041895404174217804,0.048189782170018416,0.05414314975160648,0.05954965281624295,0.0642529415407071,0.06814006127696315,0.0711324311101534,0.07317688713440156,0.07423816644742395,0.07429343929141041,0.07332915955307637,0.07134038451592274,0.06833271281427711,0.06432706745025422,0.05936771822896068,0.05353427101734819,0.046959070198077296,0.03985313576013413,0.03254767305060092,0.025565421163307407,0.019729058875169347,0.016141671914746802,0.015375948144921853,0.0164082643538013,0.01763400931092186,0.018068953450220197,0.01729443600403098,0.015158106166424502,0.011617511513642384,0.00677133011671075,0.0024305732457080916],[0.0863470399052256,0.08271367192292214,0.07849827923775084,0.07366304790422697,0.06818726191466636,0.062075898510022265,0.05537050376636249,0.04816285818335798,0.04061238972227134,0.03296969307078501,0.025612693574505702,0.019112353163718145,0.014346377380806737,0.012444866969522638,0.013756518332138581,0.017286596667574927,0.022135400443439614,0.027873589775711954,0.034182810668182254,0.04073087412241278,0.04719818210914949,0.05331201382913895,0.05885827818390349,0.06367833716091267,0.06765966647570154,0.07072517059176134,0.07282339055080965,0.07392057243668461,0.07399499189994765,0.07303369603017279,0.07103175624104387,0.06799414914860157,0.06394047251421071,0.058912878491611406,0.052987955161258544,0.04629407084198338,0.03903765141797699,0.031546997112058,0.024354620988048414,0.01834839041011631,0.01483055831673874,0.014509350733675819,0.016072288674401667,0.01768069393156384,0.018335590357637727,0.017649851412663384,0.015501932321458883,0.0118849075294427,0.00694858154372089,0.002624419039618928],[0.08652229774472481,0.08293607222448404,0.0787793887307583,0.07401692124357055,0.06863083142598918,0.0626293103746526,0.056057235990460856,0.04900920354128149,0.041645213090340666,0.03420947686336934,0.027053423595443944,0.02066559339268983,0.015713157760680645,0.013047062201446392,0.013288684576473916,0.016097434399303216,0.020669719294798338,0.026407286870086276,0.03284756528944255,0.03957250274641141,0.04621931415200825,0.05249644008971115,0.05818307138396511,0.06311939785957406,0.06719403501017686,0.07033179830822922,0.0724831846337336,0.07361609958000485,0.0737100204708743,0.07275265622103967,0.07073914628564676,0.06767388577575281,0.06357516154057263,0.05848295924010139,0.05247064928849402,0.04566206698859995,0.038257638536282154,0.030579369109760283,0.02316234965182266,0.01695354653225372,0.013491789890964338,0.013659038476593829,0.01576681777809929,0.01774184077428796,0.018599240232872787,0.017991996274365648,0.015829745319128907,0.012138454845492658,0.007113850244613591,0.0027900397142832274],[0.08670540354593448,0.08316820775924114,0.07907245148243931,0.07438528059462818,0.0690916491361942,0.06320274207545261,0.056766294212137476,0.04987877174880858,0.04269899580966913,0.03546193727011464,0.028489638268086582,0.022193989083829187,0.017073769479001227,0.013745444681619392,0.012930341973918482,0.01492185293523942,0.01917773177712455,0.02492272342882676,0.031510936188554425,0.03842468621356563,0.045257031842075725,0.05169951675824636,0.05752641925409635,0.0625779513926622,0.06674457792513218,0.06995342939878117,0.07215718692926397,0.07332554917479808,0.07343928155805375,0.07248682119994176,0.07046343573055631,0.06737299608979314,0.0632325242931082,0.058079845231862645,0.051985002275930996,0.045066884435307736,0.037518706676661386,0.029652850942460736,0.02199857939000578,0.01555050963786787,0.012127572032725761,0.01283694931664795,0.015498818113521969,0.0178201190998977,0.018861440170900877,0.018322151157447546,0.016142360137459493,0.01237785105570623,0.007264364038857474,0.0029213516473549127],[0.08689593860558903,0.0834095047535336,0.0793766792372459,0.07476704028210844,0.06956821696886147,0.06379412736161272,0.05749484567101452,0.050767752310939884,0.04376885859862469,0.03672156149428417,0.029916962791320414,0.023696883730581014,0.01842459515483559,0.014523329867324419,0.012692047065023448,0.013768456036695683,0.01765922464695088,0.02342248568227782,0.030177805925730175,0.037292416510683914,0.0443155250925827,0.050924502770220516,0.05689078796375165,0.06205585739370567,0.06631271411013324,0.06959117463152108,0.07184630400737571,0.07304970726447346,0.07318351274614608,0.07223694895377258,0.07020547757471053,0.06709251957244697,0.0629139109977489,0.05770537984171652,0.051533634035357455,0.04451237666082055,0.03682667962508631,0.028776265358942395,0.020875306082333508,0.0141475899139232,0.0107411639999586,0.012058321957579346,0.015275711743699565,0.01791832304289536,0.019123852890043137,0.018641679285287864,0.016440683787022084,0.012603024877258345,0.0073980218794402934,0.0030137583177370975],[0.08709347615355069,0.08365938087208909,0.07969127633451363,0.07516111220048098,0.07005904763460986,0.06440144109388299,0.05824016329798771,0.05167256955847597,0.0448503907901141,0.03798363659864992,0.031331972997128164,0.025173971674037923,0.019763391111730536,0.015366515037164309,0.012582552496070857,0.01264950925116267,0.01611420550584241,0.021910073018606244,0.028854068172622982,0.036181327935085605,0.04339931784319249,0.050174812967299205,0.056278708328974796,0.06155499570576857,0.0658998615589359,0.06924613383255945,0.07155142629703579,0.07278934023197119,0.07294342843333075,0.07200376977398032,0.06996609101895225,0.06683345391963334,0.06262062059768568,0.05736134646685508,0.05111910480831236,0.04400237339894692,0.036187515215582805,0.027959125577220845,0.019806841172756565,0.012756580756530002,0.009337540966766185,0.011342245079662581,0.015105125238495633,0.01803928440047761,0.01938822268872228,0.018952009101806385,0.016725725683605922,0.012814196071485475,0.007513559225529994,0.0030641153718217436],[0.08729758326874824,0.08391724804162826,0.08001544386861498,0.07556641189824104,0.07056267332887028,0.065022710973876,0.05899963923911736,0.05258989091386186,0.0459396306813722,0.03924415386714712,0.032732006280950215,0.026625222811385386,0.021088856440238442,0.01626333373556871,0.012607753921979844,0.011582385924863213,0.014542953151011334,0.020390199690172937,0.027546811656353695,0.035097737308031375,0.042513257117984066,0.04945399798274596,0.0556927583551509,0.061077253335174164,0.06550742794986658,0.06891938898043287,0.07127342275885029,0.07254519032119729,0.07271971559336869,0.07178798165915126,0.06974605577444251,0.06659674717112382,0.062353888887358766,0.05704944937252544,0.05074388248118344,0.04354062264077035,0.035607203672650946,0.027211500837047698,0.018810036093276992,0.01139465125378593,0.007924774014320405,0.010711916388251757,0.01499456471899747,0.018185781851132357,0.019656332354567905,0.019254615424881223,0.016998599586065862,0.01301191015850137,0.007610648790120739,0.0030707195877332063],[0.08750782275813314,0.08418251518701043,0.08034838365569845,0.07598186424964497,0.0710776535726372,0.06565602755024035,0.05977079513020714,0.05351662993241714,0.047033041120347174,0.040499722015409176,0.03411501560173164,0.028050827833232626,0.02240035306608346,0.017204437030630546,0.012769921862880028,0.010591429135782848,0.012946094284890262,0.018869231948024683,0.02626453095062442,0.0340486725202722,0.04166249130017908,0.04876571826457027,0.055135542961334,0.06062451009512884,0.06513680062305548,0.06861199702813706,0.07101313544507251,0.07231797112936066,0.07251302955977876,0.07159024577874737,0.06954610646570437,0.06638328995358218,0.062114876715901914,0.05677129432864621,0.050410308573993146,0.04313072713575331,0.035091644660317174,0.02654380258092179,0.017904330874180044,0.010087453468602852,0.006517199384041035,0.01019417467044498,0.0149510333706016,0.018360450191750536,0.019929961441081934,0.01955099889894145,0.017260515877332027,0.013197044218750145,0.007689935153700571,0.003033314120144111],[0.0877237549860678,0.08445459086120405,0.08068930198078915,0.07640640868248043,0.07160258217633073,0.06629955255620136,0.060551289436429824,0.054449945108126,0.048127482325171084,0.04174748965477118,0.03547945547244785,0.0294511561640129,0.023697716486560678,0.018182458936610833,0.01306744276337386,0.009709969775593928,0.011324735006022081,0.01735583327485437,0.0250173589553758,0.03304188207384209,0.04085243530325112,0.04811371180219143,0.05460967092575305,0.060198623052225314,0.06478933605238345,0.0683249825261647,0.07077137400274393,0.07210836311677939,0.07232398987741236,0.07141118205078212,0.06936692720134256,0.0661939079532222,0.061904658466004375,0.05652836943385789,0.05012056371028427,0.042776077016528705,0.0346465052505947,0.02596648059928813,0.01711146270839776,0.008874056011946825,0.005143584214923446,0.009817720141526654,0.014980624933600592,0.018565693826918146,0.020210846597823427,0.019842663915715035,0.01751276402524062,0.013370782506810727,0.007753001908881763,0.002953106111287355],[0.08794493964271984,0.08473288575274454,0.08103741310386582,0.0768390039400334,0.07213609332465806,0.06695152565998634,0.06133892218708591,0.05538723532692013,0.04922018341000557,0.04298507667699226,0.036824191787520215,0.030826722065948692,0.024981122669507423,0.019191659740310833,0.013495137546813907,0.008981516059815705,0.00968071569254594,0.01586193002942505,0.023817306424268915,0.0320858161386604,0.04008872035115581,0.04750175530821394,0.05411772919669184,0.05980140993752159,0.0644663489322166,0.06805933013043981,0.07054891018105089,0.07191700918365282,0.07215317626852262,0.07125136488758127,0.06920914638707208,0.06602935473766908,0.06172421102431025,0.056322026558904205,0.04987663350956294,0.04247978072581603,0.034277063503152676,0.025489628538365,0.016454629629507698,0.00781383692738152,0.00387087438127746,0.009609606676002379,0.015088141470543824,0.018803609034654355,0.020500644860683998,0.020131095628015898,0.017756686207672397,0.013534563156647717,0.0078022699752836235,0.002832796147152865],[0.08817093744126148,0.08501681505677036,0.08139194250827184,0.07727863236432636,0.07267686679560292,0.06761026972946083,0.06213163743602528,0.05632613273495868,0.0503087136712849,0.044210513853653065,0.038148429522964565,0.03217815621164501,0.02625099087376055,0.02022759442915604,0.014045036131888572,0.008457849516944083,0.008017174855934062,0.014404163879711298,0.022678477798691817,0.03118956761816186,0.03937712636876348,0.04693361886882702,0.05366225483421643,0.05943463173482916,0.06416910102054359,0.06781597708854872,0.07034647240841048,0.07174451036544842,0.07200112476142816,0.07111131916410449,0.06907333185564554,0.06589030504694565,0.0615744034633019,0.056153463862115956,0.04968027594348581,0.0422445969136928,0.03398804501810327,0.025122514101706808,0.015956932425038782,0.006992441807488926,0.0028753295968703663,0.009590392875822428,0.015276789765933878,0.019075919351776258,0.020800900950493115,0.020417737091619162,0.017993644221742187,0.013689999924884995,0.007840826879657365,0.0026766219286039825],[0.08840131173494936,0.08530580069816066,0.08175212987936703,0.07772430369579966,0.07322363233937908,0.06827419472571715,0.06292752376747514,0.057264493674706145,0.051390954363226896,0.04542218979353857,0.03945165395384057,0.03350618110126464,0.02750791023966773,0.021286825125971427,0.014707366380542854,0.00819091093442011,0.006340006005965061,0.013006050046663711,0.02161720784430189,0.030362760400721042,0.03872349561788373,0.04641301441632154,0.05324570498218362,0.059099974709792384,0.0638987898999977,0.06759580580572769,0.07016474050813563,0.07159142169979581,0.0718683240299709,0.07099151646250156,0.06895998638646639,0.06577734867053961,0.061455987651271006,0.05602370983296454,0.049532991248476016,0.042072870327346926,0.033783462263449054,0.024873069348577942,0.015639084431798882,0.00651534555858491,0.0025482260404361963,0.00976959822416357,0.015548003273612283,0.01938392772536083,0.021113019667281106,0.02070396788801225,0.018224982807176444,0.013838785635020882,0.007872190359347699,0.0024904204376617915],[0.08863563004644957,0.08559927339768919,0.08211723180562452,0.07817505839181779,0.07377517325343237,0.06894180034828779,0.06372481314848624,0.05820038823390848,0.05246507144619709,0.046618804379894456,0.04073358220537045,0.03481158933969586,0.028752582704940542,0.022366681406294563,0.015471513454730558,0.008218028190982395,0.004662477044007129,0.011701033764748243,0.020652030251434878,0.029615372257043512,0.038133627270714336,0.045943538787986744,0.0528704254102691,0.05879903219159813,0.06365653783537677,0.06739963659822898,0.07000434062355115,0.07145824831800292,0.0717552119910939,0.07089237164458476,0.06886954368403495,0.0656909850210847,0.06136958999593735,0.05593360930291897,0.04943599547921968,0.041966474863329675,0.03366646816022817,0.02474739603916233,0.015516708160446013,0.006471128309074864,0.003133034058664941,0.01014370247060327,0.015901415609539518,0.019728487916137724,0.02143824439002857,0.02099108576310017,0.01845199328162624,0.013982586578533076,0.007900016461778183,0.002281711560477107],[0.08887346550307279,0.08589667457442442,0.08248652419835356,0.07862997047265957,0.07433032919751217,0.06961167755802583,0.06452187840581998,0.059132088855369136,0.05352948961101261,0.04779932785772827,0.04199412280481515,0.03609522417917276,0.02998577760282057,0.02346506542210533,0.016326789076157228,0.008547688217078698,0.003025064100919402,0.010536273904069388,0.019803353750657594,0.028957482866340874,0.03761315412445303,0.045528612597848225,0.05253861830375588,0.05853328646165728,0.06344338091955841,0.06722822074553428,0.0698658404239718,0.07134544181342349,0.0716621727059682,0.07081423980069845,0.06880236487889659,0.06563161850530427,0.06131570450840105,0.055883811825139545,0.04939019871235398,0.04192676683973947,0.03363923581323848,0.024749352986807235,0.015597909669797466,0.006876692167597254,0.004284287641553085,0.010697772507368076,0.016334983089006185,0.02010999616031647,0.021777642496336007,0.02128029283107626,0.018675881796793498,0.014122939296538097,0.007927772435378486,0.0020597941630364556],[0.08911439817285866,0.08619745807980986,0.08285930442985921,0.07908814990899149,0.07488799829866814,0.07028250910341759,0.06531722957913262,0.060058058370278944,0.0545828677525947,0.048962964822738125,0.04323334151863318,0.03735796197373857,0.031208294998457033,0.024580296176607962,0.01726295385815967,0.009157095922905107,0.0016310693052349853,0.009575659625376832,0.01909270180949889,0.02839894433091983,0.037167404584301254,0.04517141662825765,0.052252310103895985,0.05830409113709217,0.06326025870810768,0.0670822339540363,0.06974974466185373,0.0712533969368587,0.07158953362716984,0.0707574136190732,0.06875873560750903,0.06559955477967076,0.061294687347732836,0.055874762766336315,0.04939618876638799,0.04195455114742849,0.03370287505146699,0.024880290021650948,0.015881959994916765,0.007666203040718084,0.005674205530794758,0.011409662404751929,0.016845227099461,0.02052840250879988,0.022132098216407305,0.021572687722275507,0.018897746485251665,0.014261162493661873,0.007958406947763537,0.0018358024818051287],[0.08935801629769043,0.08650109176093249,0.08323489319309499,0.07954874456924887,0.07544713859997791,0.07095306917297026,0.0661095093754727,0.06097693774493995,0.055624075975462206,0.0501091224563262,0.0444514322081022,0.03860069634079194,0.03242093586288816,0.025710986843513604,0.018270511990001393,0.010003405059224767,0.0015715642639852164,0.008897549982047543,0.018541402582212194,0.027948982821844257,0.03680125522445572,0.04487482790085268,0.05201332030191157,0.05811265445816317,0.06310800454545383,0.06696227034299326,0.06965649114862002,0.07118244866594757,0.07153756323046843,0.07072212121423745,0.06873886371857,0.065594997962062,0.061306752973402635,0.05590669737746629,0.04945422109824038,0.042050062269344324,0.03385739355322321,0.025138973562983655,0.016359595741340608,0.008738734138832928,0.007168842517216133,0.012254617814474332,0.017427550401923605,0.020983239795106343,0.022502313057710895,0.021869264703373196,0.01911856722486797,0.014398296865048388,0.007994061872897225,0.0016225498143831775],[0.0896039174208117,0.08680705885240297,0.08361263608872439,0.08001094174890308,0.07600676890913956,0.07162222229110372,0.06689748792365387,0.06188753376942709,0.05665217415156982,0.05123738244334655,0.045648691763108026,0.03982432391527513,0.03362447782835972,0.026855949475515162,0.019340833248978208,0.011038734322489682,0.002958358612745615,0.008579789361140643,0.01816873599456698,0.02761575493252229,0.036518981401536164,0.04464135795464168,0.05182323215314038,0.0579600238950642,0.06298733678157771,0.06686883705858666,0.06958644721209477,0.07113286969112145,0.07150646906489934,0.07070852444652875,0.0687428776430607,0.06561804885202649,0.06135197199414434,0.055979638018439276,0.04956421528137309,0.042212961271908864,0.034101706128807675,0.025521715742109305,0.017014799950557914,0.010004161950123259,0.00871563984825523,0.013208694540969597,0.018076578098319064,0.021473667030409153,0.02288881351775404,0.022170920294792052,0.01933921070525646,0.014535083956908208,0.008035877293909468,0.0014337230294956477],[0.08985170940724484,0.08711485919802162,0.0839919049479663,0.08047396930633394,0.07656596910399435,0.07228892156827123,0.06768005700180552,0.06278880686595102,0.05766639201010066,0.052347476094407444,0.0468254984117505,0.04102973163424301,0.03481965566510948,0.028014122188322027,0.020466162285806274,0.012220040959449934,0.0046524427963031394,0.008670568100530822,0.017989763941638245,0.027405898208876248,0.03632411516078512,0.04447309608363213,0.05168336629375781,0.05784707247867504,0.06289885106727015,0.06680234961374361,0.06953990669221431,0.07110486835522994,0.07149639624904545,0.07071671775735808,0.06877082545385303,0.06566870419172861,0.06143027075936891,0.05609339461056962,0.04972575818391686,0.042442348864458135,0.034433690910401764,0.02602268234215611,0.01782737193619825,0.011397420816737358,0.01029063959048767,0.01425059281294837,0.01878648187635886,0.021998523308109353,0.023291965384947114,0.022478467301552077,0.019560452014435466,0.014671991651623275,0.008083940443341904,0.0012816581763569277],[0.09010101135666566,0.08742401030497593,0.08437209890167788,0.08093709643202318,0.07712387995183212,0.07295220640837759,0.06845622388789804,0.0636798591531312,0.058666110713017944,0.05343926226989897,0.0479822928768478,0.04221778551645899,0.036007145860039114,0.029184514664384462,0.02163956451402555,0.013512604851946896,0.006422935251600678,0.009163797066469519,0.018013315975128,0.02732412758282269,0.036219320618617636,0.044371660314816264,0.05159475820313046,0.05777448723073437,0.06284301389813363,0.06676312804011317,0.06951708752381487,0.07109858707750479,0.07150742643498649,0.07074672753681628,0.06882267462853774,0.06574685697796802,0.06154143269473453,0.05624756828495253,0.049938113669761475,0.0427367936062563,0.03485028661477558,0.026634326038914444,0.018775475670887713,0.01287501367231871,0.01188106929998405,0.015362263991759089,0.019551259984149166,0.022556388054761553,0.0237119935533775,0.02279265552350921,0.01978301222074309,0.014809288639909575,0.008137416590089552,0.0011732155172895374],[0.09035145440926337,0.08773404823470518,0.08475264520783019,0.08139963407911459,0.07767970249818484,0.07361119976836124,0.06922510496154288,0.0645599228687195,0.05965084585493525,0.05451270776766244,0.04911956197671226,0.04338932091177001,0.03718755481945848,0.030366168492540948,0.02285484309078651,0.014889783919357504,0.008224900312507357,0.010003855063921138,0.018240717917842902,0.027372932794092367,0.03620629676354361,0.04433815870429711,0.051558140356734415,0.05774276002156015,0.06282015755293915,0.06675139392446286,0.06951812994601621,0.07111410128526399,0.07153957725434038,0.07079851203170034,0.06889831251653325,0.06585229781364832,0.06168510133900394,0.05644155809145248,0.05020023836478679,0.043094373430917474,0.03534762149176526,0.02734787830983767,0.019837623624923237,0.014408196747192766,0.013479152111840925,0.01652881402770361,0.020364959829645493,0.023145643641713076,0.02414900598207518,0.02311419779023117,0.02000760960858928,0.014947163912038238,0.008194873371983592,0.0011054863298240155],[0.09060268244600324,0.08804452833577456,0.08513299985088324,0.08186093508412853,0.07823269707893113,0.07426510505639493,0.06998591916601477,0.06542834922625747,0.06062023181780931,0.055567869890690604,0.05023782435925201,0.044545134194088995,0.03836141029837611,0.0315581294251318,0.024106448257105912,0.01633146736286628,0.010043277276749881,0.011114145246380255,0.018665691917506225,0.027552422720906324,0.03628571600986443,0.044373163087142634,0.05157392975969179,0.0577521811192968,0.06283047654144258,0.06676726838518586,0.06954309536726815,0.07115141886885833,0.07159280225340796,0.07087196179330833,0.06899754749893496,0.06598471726553076,0.06186078499687295,0.05667457053758536,0.050510802785865276,0.04351272795169029,0.03592116256588155,0.028153836948345796,0.02099392644731462,0.015977627712630074,0.015079622047860496,0.017738103469141602,0.0212218416393828,0.023764536869967726,0.024603020238296164,0.023443799443730574,0.020235020567272676,0.015085880848143118,0.008254771937260446,0.0010663203928655493],[0.09085435268550786,0.08835502582512869,0.08551264792759017,0.0823203940068486,0.07878218200709798,0.07491320274678812,0.07073798142220891,0.06628459775955571,0.06157400740768229,0.056604880956355456,0.05133761812472978,0.04568597586399668,0.039529155702056194,0.03275942910387235,0.025389390617450124,0.01782243344727692,0.011870764450630204,0.012422630610508998,0.01927545452940197,0.02786034122760023,0.036457203956972196,0.04447669676067592,0.05164222134716476,0.05780283561647347,0.06287402564143138,0.06681077102610766,0.06959196590380795,0.07121048016704072,0.07166699131684194,0.07096690065566262,0.0691201108173534,0.06614370917484125,0.06206786288393583,0.05694563164450043,0.050868216939185175,0.04398911856990057,0.036565873453002634,0.029042401552973558,0.022226700204047475,0.017569893082396357,0.01667861152050581,0.018980273482581456,0.02211648897905562,0.02441123653356093,0.02507399098996623,0.023782189026836462,0.02046614484886269,0.01522595007884624,0.008316058945319003,0.0010417635798702107],[0.09110613618048015,0.08866513622494625,0.08589110383448194,0.08277744671819606,0.07932753198290164,0.0755548467815249,0.07148069607104317,0.06712822619173267,0.06251200270044648,0.05762393454553018,0.05241949014007617,0.04681254501525941,0.04069114692796858,0.03396907419976717,0.02669916367503019,0.019351008312131723,0.013702806874710462,0.013872343252929046,0.020052623348207167,0.028292250824402992,0.03671936203843143,0.04464823676972055,0.05176278749832158,0.057894602831329134,0.06295071956605283,0.06688181988499085,0.06966464459742948,0.07129115848143093,0.07176197157169892,0.07108308722641453,0.0692656590365552,0.06632877484901735,0.062305592606952134,0.05725360114261862,0.05127065936776899,0.04452049325284169,0.03727637016351044,0.030003829436503805,0.0235206237594001,0.019175375164642416,0.018273105747832544,0.020247304091488772,0.023043875472844352,0.02508388503330872,0.025561836854321906,0.024130147765163715,0.02070206917298206,0.015368301954327116,0.008378768750044513,0.001025704873431318],[0.09135771821720767,0.08897447566300362,0.08626791127273534,0.08323156976433889,0.07986817627244944,0.0761894608205781,0.07221355040750539,0.06795888085199164,0.06343412702518059,0.05862527331980398,0.05348398688155126,0.04792548510619532,0.04184765142856708,0.03518604124858725,0.02803167728504092,0.020908072870939407,0.015536051222520535,0.0154215914812221,0.020977352802579063,0.02884185328261643,0.03706983069846083,0.04488673057964252,0.051935083652738925,0.05802715868772141,0.06306033426203317,0.06698023237376445,0.06976095630646334,0.071393261110293,0.07187750875640889,0.07122021686479647,0.06943377709539926,0.06653932804719634,0.06257311879632937,0.05759718838483423,0.05171610856973009,0.04510355295640216,0.03804706642695528,0.031028702927276115,0.02486263229079175,0.02078695040823453,0.019860654036406276,0.021532641569940093,0.023999397825366076,0.025780642756268988,0.026066465156226917,0.024488535472289852,0.020944123053042316,0.015514438795624247,0.008444543056343567,0.001027833030587243],[0.09160879862221241,0.08928268104498498,0.08664264308633302,0.08368227953442102,0.0804035966972412,0.07681653439578472,0.072936108357955,0.06877628765262087,0.06434035801617709,0.059609178258915305,0.05453164666647115,0.04902538096344824,0.04299884918435074,0.03640927575489715,0.029383201772060694,0.022486356730531957,0.017367764121797868,0.017040646814618275,0.02202920886828125,0.029501397991205516,0.03750538709013669,0.0451906260648141,0.05215825976149162,0.05819998098376825,0.06320250979903055,0.06710572718729672,0.0698806492520827,0.07151653088368119,0.07201330903230777,0.07137792411383195,0.06962398189164165,0.06677470065940982,0.06286948268901107,0.05797496953152563,0.05220237571593918,0.04573481699071775,0.038872302655807385,0.03210811256979608,0.026241684025417367,0.022399184600570107,0.021439206680289508,0.02283089914290311,0.024978884392976096,0.026499724591810308,0.026587793380515465,0.024858310752949964,0.021193921249161345,0.015666549104995514,0.008516990180847646,0.001077033432907521],[0.09185909198054963,0.08958941010755828,0.08701490094942174,0.0841291312581963,0.08093332547324188,0.07743561901620222,0.07364800434224694,0.06958024363028933,0.06523073166780645,0.06057595918959877,0.05556299315148919,0.05011275693353508,0.044144835286518,0.0376376943923649,0.0307503215924851,0.02407994341258976,0.019195580270820294,0.018708282536079403,0.023188529852972435,0.030262123169064237,0.03802206862614332,0.04555791299820778,0.05243117706924272,0.05841235737097004,0.06337675477185677,0.06725792713821171,0.07002339719085064,0.0716606481743702,0.07216902120909909,0.07155578554776704,0.06983572633888695,0.06703414897016784,0.06319363244907315,0.05838540555837612,0.05272713765991175,0.046410685095737626,0.03974645523327386,0.03323376852017991,0.027648485824314565,0.024007824556272053,0.02300701729254072,0.024137622293101228,0.025978586967623833,0.02723942848917756,0.02712576639268155,0.0252405437986561,0.021453388332592808,0.015827570049013424,0.008601827817808716,0.0012128898289640005]],[],[],[[0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671,0.7950389726501671],[0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427,0.789014991626427],[0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849,0.7827304934328849],[0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029,0.7762498694865029],[0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565,0.769656193664565],[0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809,0.763052064313809],[0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478,0.7565592182397478],[0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678,0.7503163468648678],[0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726,0.7444745067452726],[0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537,0.739189657760537],[0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903,0.7346123595442903],[0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009,0.7308756510710009],[0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596,0.7280834069034596],[0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666,0.7263020527673666],[0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703,0.7255572332555703],[0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533,0.725834031445533],[0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961,0.7270766867042961],[0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295,0.7291844544644295],[0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085,0.732011492181085],[0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823,0.7353840929557823],[0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022,0.7391233630940022],[0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403,0.7430618739281403],[0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371,0.7470543477822371],[0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835,0.7509841383518835],[0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427,0.7547669318863427],[0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275,0.7583527238693275],[0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672,0.7617268194798672],[0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433,0.7649103578432433],[0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741,0.7679606544765741],[0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577,0.770971476996577],[0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734,0.7740731997528734],[0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401,0.7774326069485401],[0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687,0.781251913167687],[0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994,0.7857663246975994],[0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371,0.7912391500866371],[0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612,0.7979530532921612],[0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794,0.8061954887385794],[0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474,0.8162356198924474],[0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393,0.8282890847896393],[0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713,0.8424661387872713],[0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253,0.8587010416050253],[0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176,0.8766818053436176],[0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708,0.8958416597157708],[0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576,0.915435279955576],[0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598,0.9346402251033598],[0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128,0.9526438519148128],[0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547,0.9687112178286547],[0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983,0.9822374122234983],[0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601,0.9927886886526601],[1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346,1.0001365372661346]],[[0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296,0.09070631441120296],[0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668,0.08817244796438668],[0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464,0.08528949607445464],[0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205,0.08205044877552205],[0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963,0.07845949952032963],[0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258,0.07453280733622258],[0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005,0.07029679996807005],[0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388,0.0657825521607388],[0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929,0.06101500753789929],[0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273,0.05599721778040273],[0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288,0.05069305048158288],[0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857,0.04501683497319857],[0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452,0.03884313856350452],[0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646,0.032051886259803646],[0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196,0.024631381440600196],[0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074,0.01694038116770074],[0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391,0.010795238837866391],[0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114,0.011632743422470114],[0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905,0.018895390259791905],[0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248,0.027663909835424248],[0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465,0.036345259924468465],[0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461,0.04440752730820461],[0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854,0.05159570663184854],[0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726,0.05776805443587726],[0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307,0.06284439187206307],[0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213,0.06678184376777213],[0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087,0.06956033416435087],[0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095,0.07117311914151095],[0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599,0.07162083102646599],[0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738,0.07090847795974738],[0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909,0.06904522540656909],[0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409,0.06604701615113409],[0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451,0.06194232041964451],[0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224,0.056781677293538224],[0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304,0.050652451090724304],[0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197,0.043702098094497197],[0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613,0.03617840848192613],[0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157,0.028510403754595157],[0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254,0.021493387379338254],[0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526,0.01663135511174526],[0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075,0.01573863446286075],[0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107,0.018246282348643107],[0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603,0.021586080934695603],[0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549,0.02402765930107549],[0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304,0.024794969939787304],[0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386,0.02358207936436386],[0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013,0.020329717043348013],[0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308,0.015143371779950308],[0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184,0.008279877654892184],[0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072,0.0010550607563014072]],[],[]]},{"xaxis.title":"gamma","xaxis2.title":"gamma","xaxis.range":[-6.0,3.0],"xaxis2.range":[-6.0,3.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.29,"yanchor":"middle"},{"buttons":[{"args":[{"visible":[false,false,false,false,true,true,true,true]},{"yaxis.title":"gamma","yaxis.range":[-6.0,3.0],"yaxis2.range":[-6.0,3.0],"yaxis.type":"log","yaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.43,"yanchor":"middle"}],"xaxis":{"anchor":"y","autorange":false,"domain":[0.05,0.45],"exponentformat":"e","range":[-9.0,1.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis":{"anchor":"x","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,3.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"gamma"},"type":"log"},"xaxis2":{"anchor":"y2","autorange":false,"domain":[0.6,1],"exponentformat":"e","range":[-9.0,1.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis2":{"anchor":"x2","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,3.0],"tickfont":{"size":11},"tickmode":"auto","type":"log"},"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Comparison

In [94]:
max_accuracy = {"Method": [], "Trial": [], "Accuracy": []}
for k, v in results_svc.items():
    max_accuracy["Method"].extend([k] * (len(v) + 1))
    max_accuracy["Trial"].extend([0] + (v.trial_index + 1).to_list())
    max_accuracy["Accuracy"].extend([0] + v["accuracy"].cummax().tolist())
render_plotly_html(px.line(max_accuracy, x="Trial", y="Accuracy", color="Method"))

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="4a64f45f-a17f-4001-9caa-52276600a664" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("4a64f45f-a17f-4001-9caa-52276600a664")) {                    Plotly.newPlot(                        "4a64f45f-a17f-4001-9caa-52276600a664",                        [{"hovertemplate":"Method=PI\u003cbr\u003eTrial=%{x}\u003cbr\u003eAccuracy=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"PI","line":{"color":"#636efa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"PI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,0.72,0.86,0.86,0.97,1.0,1.0,1.0,1.0,1.0,1.0],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=EI\u003cbr\u003eTrial=%{x}\u003cbr\u003eAccuracy=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"EI","line":{"color":"#EF553B","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"EI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,0.72,0.86,0.86,1.0,1.0,1.0,1.0,1.0,1.0,1.0],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"Trial"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"Accuracy"}},"legend":{"title":{"text":"Method"},"tracegroupgap":0},"margin":{"t":60}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>